<center> <img src = "img\logo.png" alt="drawing" style="width:400px;">

<center>  

<span style="background-size: 600px;background:White;color:REd;font-size: 60px;font-family: Comic Sans MS">Кредитный скоринг Альфа банка</span>

# <span style="color:DeepSkyBlue">Задача</span>

**Задача**

Кредитный скоринг – важнейшая банковская задача. Стандартным подходом к ее решению   
является построение классических моделей машинного обучения, таких как логистическая   
регрессия и градиентный бустинг, на табличных данных, в том числе используя агрегации  
от каких-нибудь последовательных данных, например, транзакционных историй клиентов.   
Альтернативный подход заключается в использовании последовательных данных “как есть”,   
подавая их на вход рекуррентной нейронной сети.

В этом соревновании участникам предлагается решить задачу кредитного скоринга клиентов   
Альфа-Банка, используя только данные кредитных историй. [Источник](https://www.kaggle.com/competitions/alfa-bank-pd-credit-history)

**Данные**

Датасет соревнования устроен таким образом, что кредиты для тренировочной выборки взяты   
за период в М месяцев, а кредиты для тестовой выборки взяты за последующие K месяцев.

Каждая запись кредитной истории содержит самую разнообразную информацию о прошлом кредите   
клиента, например, сумму, отношение клиента к кредиту, дату открытия и закрытия, информацию   
о просрочках по платежам и др. Все публикуемые данные тщательно анонимизированы.

Целевая переменная – бинарная величина, принимающая значения 0 и 1, где 1 соответствует   
дефолту клиента по кредиту.


**Проверка решений**

Метрика соревнования – ROC AUC. Подробнее про метрику можно почитать, например, [здесь](https://dyakonov.org/2017/07/28/auc-roc-площадь-под-кривой-ошибок/).

# <span style="color:DeepSkyBlue">Используемые библиотеки</span>

In [1]:
import os

# работа с регулярными выражениями
import re

# библиотеки для работы с табличными данными
import pandas as pd
import pyarrow as pa
import pyarrow.parquet as pq
import fastparquet as fp

# генерация случайных чисел
import random
from random import randint
from sklearn.utils import shuffle

# библиотеки для построения графики
import seaborn as sns
import matplotlib.pyplot as plt #для визуализации
import plotly.graph_objects as go
import plotly.figure_factory as ff
import plotly.express as px
from plotly.subplots import make_subplots
import nbformat

# библиотеки для математических преобразований с массивами данных
import numpy as np
import mlx.core as mx
from sklearn import model_selection
from sklearn.model_selection import train_test_split

# библиотеки для работы с функциями(частичная передача аргументов в функцию)
from functools import partial

# библиотеки для работы со статистическими характеристиками
from scipy import stats
import statistics
from collections import Counter

# библиотеки для работы с pipeline
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import FunctionTransformer

# проверка временного ряда на статичность
from statsmodels.tsa.stattools import adfuller

# Импортируем DBSCAN-кластеризацию
from sklearn.cluster import DBSCAN

# вставить картинку в Jupiter Notebook
from IPython.display import Image

# линейные модели машинного обучения
from sklearn import linear_model

# ансамбли моделей машинного обучения
from sklearn.ensemble import RandomForestClassifier
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.ensemble import HistGradientBoostingClassifier

# поиск гиперпараметров модели
from sklearn.model_selection import RandomizedSearchCV
from sklearn.feature_selection import SelectKBest, f_classif
from sklearn.feature_selection import RFE
import optuna

 # метрики
from sklearn import metrics

# библиотека для стандартизации данных
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import RobustScaler

# сохранить полученные модели
import joblib
from joblib import dump, load

# сборщик мусора
import gc

# для ограничения времени выполнения функции
import signal
import func_timeout

# для отслеживания времени выполнения функции
import time

# очистить output
from IPython.display import clear_output

## <span style="color:DodgerBlue">Разработка инструментов преобразования данных</span>

### <span style="color:RoyalBlue">функция torow_transformer</span>

In [2]:
# функция torow_transformer

# Назначение: Преобразование признака столбца в признаки строки
#               с сохранением обратной последовательности в признаке.
#               (извлечение последних операций клиента)

# Внешние переменные функции: DataFrame, n_last
#   DataFrame - исоходый DataFrame
#   n_last - необходимое счисло послдених операций клиента
#   Структура DataFrame:
#       1. id
#       2. feature1
#       3. feature2
#       4. feature3
#       ...

# Результат работы функции: New DataFrame
#   Признаки New DataFrame:
#       1. id
#       2. feature1.1
#       3. feature1.2
#       4. feature1.3
#       ...
#       5. feature1.N
#       6. feature2.1
#       7. feature2.2
#       ...
#       8. feature2.N
#       ...
#   где featureX.1 - соотвествует последней операции клиента,
#       featureX.2 - соотвествует предпоследней операции клиента,
#       .....

# 2. dict_features - словарь (карта) признаков,
#    в котором отображается сокращения признаков и их расщифровка

# Алгоритм работы функции:
# 1. извлекаем признаки из данных DataFrame
# 3. формируем карту признаков dict_features:
#    3.1. каждый признак кодируется следующим образом: 'fn',
#         где n - порядковый номер признака
#    3.2. полные имена признаков задаются следующим образом: 'feature_N',
#         где N - порядок клиентской операции (большему N соотвествует, более ранняя операция)

# 4. Преобразуем данные к массиву
# 5. Группируем массив для каждого клиента
# 6. К групированному массиву прменяем следующие преобразования:
#    6.1. Обращаем порядок клиенских операций
#    6.2. выбираем посление n_last операций
#    6.3. Если число клиенски операций меньше чем n_last, дополняем их нулями
# 7. Преобразуем полученные данные к DataFrame

# Описание локальных переменных функции:
# 1. pd_data - исходный DataFrame
# 2. n_last - необходимое число последних операций клиента
# 3. list_id - список для хранения id клиентов внутри функции
# 4. list_features - список для хранения признаков исхдного dataframe внутри функции
# 5. dict_features - локальная карта признаков
# 6. rn_id - список количества операций для каждого клиента
# 6. array_data - данные преобразоанные к numpy-массиву
# 6. split_array - сгрупированные по клиентам данные преобразованные

# обьявлем функцию
def torow_func(dict_params):
    pd_data = dict_params['data']
    n_last = dict_params['n_last']

    # извлекаем список "id" клиентов
    list_id = pd_data['id'].unique().tolist()
    
    # извлекаем список признаков из данных        
    list_features = pd_data.columns.drop(['id','rn'])

    # формируем словарь для зашифрованных признаков
    dict_features = {}
    
    # заполним словарь dict_features
    num_f=0
    for feature in list_features:
        # шифруем признак: fk = "feature_agg_function"
        for num_feature in range(1,n_last+1):
            dict_features['f'+str(num_feature+num_f)] = feature+'_'+str(num_feature)
        num_f+=n_last
    

    # формируем словарь rn_id
    rn_id = pd_data.groupby('id')['id'].count().to_list()

    # для улучшения производительности преобразуем DataFrame в array-массив
    array_data = np.array(pd_data.iloc[:,2:]).transpose()

    # "порежем массив" по длине кредитной истории клиента
    split_array = np.array_split(array_data, np.cumsum(rn_id),axis=1)
    
    # определим порядок последующих преобразований в функции
    def transform_array(array_id):
        # обратим порядок клиентских операций 
        reverse_array_id = array_id[::,::-1]
        # выбрем после n операций клиента
        list_n_last = reverse_array_id[::,:n_last]
        # если клиенских операций было меньше чем n_last
        # дополним недастающие нулями и преобразуем данные к строке
        if len(list_n_last[0])<n_last:
            full_list_n_last = np.hstack((list_n_last,np.zeros((list_n_last.shape[0],n_last-len(list_n_last[0])),dtype='int64')))
            # преобразуем список к строке
            full_list_n_last = full_list_n_last.reshape(-1)
        else:
            full_list_n_last = list_n_last.reshape(-1)
        return full_list_n_last

    # применим transform_array преобразование к списку split_array
    list_data = np.array(list(map(transform_array,split_array)))[:-1]
    
    # преобразуем полученные данные к dataframe
    dataframe = pd.DataFrame(data=list_data, columns=dict_features.keys())

    # добавим столбец id
    dataframe.insert(0,'id',list_id)
    
    return dataframe, dict_features,rn_id


# преобразуем функции в инструмент для преобразования данных (Transformer)
torow_transformer = FunctionTransformer(torow_func)

In [3]:
# функция features_from_transform_data_torow

# Назначение: Извлечение из данных, над которомы совершено 
#             row_fich_transformer() преобразование, признаков  
#             соотвествующих заданному числу последних  
#             опреаций клиента n_last

# Внешние переменные функции: DataFrame
#   Признаки DataFrame:
#       1. n_last - необходимое число последних операций клиента
#       2. n_groups - число групп признаков в transform_data_torow
#       3. N_last - число последних операций клиента показанных в transform_data_torow

# Результат работы функции: 
# 1. list_n_last_features - список признаков в transform_data_torow
#    соотвествующий заданному числу n_last. 
    

# обьявлем функцию
def features_from_transform_data_torow(n_last,n_groups,N_last):
    # создадим список под необходимые признаки
    list_n_last_features = []
    
    # обьявим начальное значение в группе признаков
    n_start = 0
    
    for i in range(n_groups):
        for n in range(n_last):
            list_n_last_features.append(n+n_start)
        n_start+=N_last
    
    return list_n_last_features   

### <span style="color:RoyalBlue">функция diff_feature</span>

In [4]:
# функция diff_feature

# Назначение: Определение дифференциальных характеристик ряда 

# Внешние переменные функции: 
#           1.Series/np.array/list


# Результат работы функции: 
# 1. diff_list - Список из значений:
#                   1.1. speed - скорость изменения ряда;
#                   1.2. accel - ускорение изменения ряда;
#                   1.3. bias - смещение ряда;
#                   1.4. pulse - импульс ряда;

# обьявлем функцию
def diff_feature(data):
    # преобразуем данные к numpy массиву
    data = np.array(data)
    # расчитаем необходимые характеристики
    speed = round(float(np.diff(data,1).mean()),2)
    accel = round(float(np.diff(data,2).mean()),2)
    bias = round(float(np.diff(data,1).sum()),2)
    pulse = round(float(np.diff(data,2).sum()),2)
    # сформируем из найденных значений в список
    diff_list = [speed,accel,bias,pulse]
    return diff_list

### <span style="color:RoyalBlue">функция statistic_features</span>

In [5]:
# функция statistic_features

# Назначение: Извлечение основных статистических характеристик
#             из признаков в исходном DataFrame.

# Внешние переменные функции: DataFrame
#   Признаки DataFrame:
#       1. id
#       2. feature1
#       3. feature2
#       4. feature3
#       ...

# Результат работы функции: 
# 1. dataframe - таблица с данными. 
#    Признаки dataframe:
#       1. id
#       2. feature1_mean
#       3. fearture1_hmean
#       4. feature1_std
#       5. feature1_min
#       6. feature1_25%
#       7. feature1_50%
#       8. feature1_75%
#       9. feature1_max
#       10. feature1_mode
#       11. feature1_frequency_mode
#       12. feature2_mean
#       ...
    
# 2. dict_features - словарь (карта) признаков,
#    в котором отображается сокращения признаков и их расщифровка

# Алгоритм работы функции:
# 1. извлекаем признаки из данных
# 2. формируем карту признаков:
#    2.1. каждый признак кодируется следующим образом: 'fn' где n - порядковый номер признака
#    2.2. полные имена признаков задаются следующим образом:
#         2.2.1 если в исходном dataframe признак бинарный, то: "Исходное имя признака"+"binary"
#         2.2.2 если в исходном dataframe признак не бинарный, то: "Исходное имя признака"+"Статистическая характеристика"
# 3. для каждого клиента по каждому признаку из исходного dataframe расчитываем статистические характеристики
# 4. записываем полученные значение в новый dataframe

# Описание локальных переменных функции:
# 1. dict_agg_function - словарь из агригирующих функций
#       keys: имена для обращения к функциям:
#       values: lamda-функция, соотвествующей статистической характристики
# 2. list_features - список для хранения признаков исхдного dataframe внутри функции
# 3. list_id - список для хранения id клиентов внутри функции
# 4. dict_features - локальная карта признаков
# 5. k - номер признака в dict_features на текущей итерации
# 6. dataframe - результирующий dataframe

# обьявлем функцию
def statistic_features(pd_data):
    # формируем список из функций для статистических преобразований
    # предусмотрим работу функций на случай, если в массиве данных всего 1 строка
    dict_agg_function = {
    'ptp' : lambda x: 0 if len(x) <= 3 else np.ptp(x),
    'mean': lambda x: 0 if len(x) <= 3 else x.mean(), 
    'gmean' : lambda x: stats.gmean(x),   
    'hmean': lambda x: stats.gmean(x),
    'pmean25': lambda x: stats.pmean(x,25),
    'pmean50': lambda x: stats.pmean(x,50),
    'pmean75': lambda x: stats.pmean(x,75),
    'expectile25': lambda x: stats.expectile(x,0.25),
    'expectile50': lambda x: stats.expectile(x),
    'expectile75': lambda x: stats.expectile(x,0.75),
    'moment': lambda x: stats.moment(x),
    'std': lambda x: 0 if len(x) <= 3 else np.std(x),
    'min': lambda x: min(x),
    '20%': lambda x: x.mean() if len(x) <= 3 else np.percentile(x,q=20),
    '30%': lambda x: x.mean() if len(x) <= 3 else np.percentile(x,q=30),
    '40%': lambda x: x.mean() if len(x) <= 3 else np.percentile(x,q=40),
    '50%': lambda x: x.mean() if len(x) <= 3 else np.percentile(x,q=50),
    '60%': lambda x: x.mean() if len(x) <= 3 else np.percentile(x,q=60),
    '70%': lambda x: x.mean() if len(x) <= 3 else np.percentile(x,q=70),
    'max': lambda x: max(x),
    'mode': lambda x: statistics.mean(statistics.multimode(x)),
    'frequency_mode': lambda x: round(list(x).count(statistics.multimode(x)[0])*len(statistics.multimode(x))/len(x),2),
    'cov' : lambda x: 0 if len(x) <= 3 else np.cov(x),
    'histogram' : lambda x: 0 if len(x) <= 3 else np.histogram(x)[1].mean(), 
    'speed': lambda x: 0 if len(x) <= 3 else diff_feature(x)[0],
    'accel': lambda x: 0 if len(x) <= 3 else diff_feature(x)[1],
    'bias': lambda x: 0 if len(x) <= 3 else diff_feature(x)[2],
    'pulse': lambda x: 0 if len(x) <= 3  else diff_feature(x)[3]
    } 

    # напишем функцию для преобразования массива до статистических характеристик
    def stat_func(array_data): 
        # сформируем лист под результаты преобразования
        list_for_result = []
        # запишем все статистические харкетристики из словаря dict_agg_function
        for func in dict_agg_function.values():
            list_for_result.append(func(array_data))
        return np.array(list_for_result).round(3)

    # напишем функцию для применения функции stat_func к списку
    def submap(list_data):
        # расчитаем количество операция клиента
        max_rn = len(list_data[0])
        # получим статистические характристики массива
        list_stat_features = np.array(list(map(stat_func,list_data))).reshape(-1)
        return np.hstack((max_rn,list_stat_features))
    
    # извлекаем список "id" клиентов
    list_id = pd_data['id'].unique().tolist()

    # извлекаем список признаков из данных        
    list_features = pd_data.columns.drop(['id','rn'])
    
    # формируем словарь для зашифрованных признаков
    dict_features = {'f1':'count'}
    k=1 # порядковый номер защифрованного признака

    # заполним словарь dict_features
    for feature in list_features:
        # шифруем признак: fk = "feature_agg_function"
        for key_function in dict_agg_function.keys():
            k+=1
            dict_features['f'+str(k)] = feature+'_'+key_function

    # формируем список rn_id
    rn_id = pd_data.groupby('id')['id'].count().to_list()

    # для улучшения производительности преобразуем DataFrame в array-массив
    array_data = np.array(pd_data.iloc[:,2:]).transpose()

    # "порежем массив" по длине кредитной истории клиента
    split_array = np.array_split(array_data, np.cumsum(rn_id),axis=1)[:-1]

    # получем статические характеристики признаков
    stat_features = np.array(list(map(submap,split_array)))
    
    # Сформируем dataframe из полученных данных
    dataframe = pd.DataFrame(data=stat_features, columns=dict_features.keys())

    # добавим столбец id
    dataframe.insert(0,'id',list_id)

    return dataframe, dict_features

# преобразуем функции в инструмент для преобразования данных (Transformer)
stat_transformer = FunctionTransformer(statistic_features)

### <span style="color:RoyalBlue">функция corr_transform_to_force</span>

In [6]:
# функция corr_transform_to_force

# Назначение: из матрицы взаимных корреляций
#             выделить не корелирующие признаки

# Внешние переменные функции: 
#           1. df.corr() - матрица корреляций
#           2. threshold - порог значимости корреляции:
#               значение коэффициента корреляции, больше которого
#               признаки считаются скоррелированными.

# Пояснение: 
# Под силой корреляции будем понимать следующее: если коэффициент 
# коррелиции между признаками больше значения threshold, то принимаем,
# что между признаками сильная корреляционная связь значение коэффициента 
# коррелияции заменяем на 1, иначе корреляционная связь слабая и значение 
# коээфициента корреляции заменяем на 0

# Результат работы функции: 
# 1. corr_matrix - матрица корреляций(отражает силу корреляции)
# 2. list_ncorr_features - список не скореллированных признаков
# 3. corr_force - сила корреляции всей матрицы: отношение числа скоррелированных 
# признаков к числу всех признаков в матрице

# Описание локальных переменных функции:
# 1. coor_force - функция преобазующая значение
#        коэффициента корряляции в силу корреляции
# 2. corr_matrix - матрица отражающая силу корряляции между признаками
# 3. max_corr - максимальное число взаимных корреляций между признаками
# 4. list_ncorr_features - список не коррелируемых признаков


# обьявлем функцию
def corr_transform_to_force(matrix,threshold=0.7):
    list_features = matrix.index.tolist()
    
    
    # создадим функцию для разметки матрицы корреляции
    # 1 - корреляция признаков выше порога значимости threshold
    # 0 - корреляция признаков ниже порога значимости threshold
    corr_force = lambda x: 1 if x >threshold else 0
    # выполним разметку матрицы корреляции
    corr_matrix = matrix.map(lambda x: corr_force(x))
    
    # алгоритм отбора не коррелиарных признаков:
    #   1. Найдем признак с наибольшим числом взаимных корреляций
    #   2. удалим найденный признак
    #   3. составим матрицу корреляций из отсавшися признаков
    #   4. повторяем пункты 1-3 до тех пор пока в матрице не останутся 
    #       не коррелированные признаки

    # ищем наибольшее число взаимных корреляций среди признаков
    max_corr = corr_matrix.sum().max()

    while max_corr > 1:
        # определяем признак с наибольшим числом взаимных корреляций
        max_corr_feature = corr_matrix.sum()[corr_matrix.sum()==corr_matrix.sum().max()].index[0]
        # удалем признак из матрицы корреляций
        corr_matrix = corr_matrix.drop(max_corr_feature).drop(max_corr_feature,axis=1)
        max_corr = corr_matrix.sum().max()
    # запишем не скоррелированные признаки в список
    list_ncorr_features = corr_matrix.index.tolist()
    # найдем силу корреляции всей матрицы как отношение
    # количества скоррелированных признаков к всмеу количеству признаков
    corr_force = round(1-len(list_ncorr_features)/len(list_features),3)
    return corr_matrix, list_ncorr_features, corr_force

### <span style="color:RoyalBlue">функция search_DBSCAN_parameters</span>

In [7]:
# функция search_DBSCAN_parameters

# Назначение: Для подбора eps и min_samples параметров,
#               функция "прогоняет" DBSCAN кластеризацию 
#               с параметрами eps и min_samples
#               примающими значения из заданного диапазона.

# Внешние переменные функции: 
#           1. data - dataframe для кластеризации
#           2. r1 - начало диапазона
#           3. r2 - конец диапазона  
#           4. n - предпалагамое число кластеров      

# Результат работы функции: 
# 1. data_cluster - кластеризация данных при различных 
#       значениях параметров eps и min_samples

# Описание локальных переменных функции:
# 1. parametr_range - диапазон изменения параметров
# 2. dataframe_columns - колонки в результирующем dataframe
# 3. data_cluster - результрующий dataframe
# 4. index_cluster - текущая позиция в data_cluster
# 5. clustering - кластеризатор
# 6. list_cluster_values - список для заполнения текущими 
#                          значениями data_cluster

# обьявлем функцию
def search_DBSCAN_parameters(dataframe,r1,r2,n=3):
    # задаем диапозон измениния параметров
    parameter_range = range(r1,r2)
    # формируем заготовку для результирующего dataframe
    dataframe_columns = ['eps','min_samples',-1,0,1]
    # проверим что задано не меньше минимального количества кластеров
    if n<=3: 
        data_cluster = pd.DataFrame(columns=dataframe_columns)
    else: 
        for claster in range(4,n+1):
            dataframe_columns.append(claster-2)
        data_cluster = pd.DataFrame(columns=dataframe_columns)
    # задаем начально значение индекса в data_cluster
    index_cluster = 0

    # для подсчета обьектов в кластерах создадим dataframe
    dataframe_count = pd.DataFrame()
    
    # "прогоняем" DBSCAN кластеризациию по диапазону параметров
    for eps in parameter_range:
        
        for min_samples in parameter_range:
            print('current eps:',eps,'  current min_samples:', min_samples, end='\r')
            # запускаем кластеризацию с текущими параметрами
            clustering = DBSCAN(eps=eps, min_samples=min_samples).fit(dataframe)
            # добавлем к данным столбец с разметкой
            dataframe_count['clater'] = clustering.labels_
            # формируем пустой список для заполнения
            list_cluster_values = []
            # добавлеям в список текущие параметры
            list_cluster_values.append(eps)
            list_cluster_values.append(min_samples)
            # добавлем в список количество обьктов в каждом кластере
            for column in dataframe_columns[2:]:
                list_cluster_values.append(len(dataframe_count['clater'][dataframe_count['clater']==column]))
                
            # заполняем dataframe  текущими данными
            data_cluster.loc[index_cluster] = list_cluster_values
            index_cluster +=1
            # сбрасываем dataframe_count
            dataframe_count = pd.DataFrame()
    return data_cluster

### <span style="color:RoyalBlue">функция generate_samples</span>

In [8]:
# функция generate_samples

# Назначение: для генерации индексов выборок данных

# Внешние переменные функции: 
#           1. max - определяет максимальное значение множества
#               из которого формируются выборки
#           2. n - количество выборок
#           3. k - мощность одной выборки
     

# Результат работы функции: 
# 1. samples_list - список с выбороками

# алгоритм работы:
# 1. задаем отрезок натурального ряда N мощностью max и добавлем в него 0.
#       In = N U {0}, I = {0,1,2,3,4,5,..,max}
# 2. если мощность множества In больше, необходимого количества элементов
#       cardo(In) > n x k , то из множества In формируем n случайных выборок
# размера k без повторения.
# 3. если мощность множества In меньше, необходимого количества элементов
#       cardo(In) < n x k , то из множества In формируем случайные выборки
# размера k без повторения, до тех пор пока не закончится множество In.
# После, добираем недостающее количество выборок случайными выборками 
# размера k из множества In с повторением (bootstrap метод).


# обьявлем функцию
def generate_samples(max,n,k,random_state = None):
    # создадим список под результат
    samples_list = []
    # формируем множество натуральных числе от 0 до max
    In = list(range(max+1))
    # Будем выполнять код пока не наберем необходимого количества выборок
    # нарушим порядок в множестве
    In = shuffle(In,random_state=random_state)
    # random.shuffle(In)

    # задаим границы извлечения данных из In
    In_start = 0
    In_end = k
    while len(samples_list) < n:
        # сформируем список под одну выборку
        sample = []
        # первые списки будем наполнять значениеми из множества In
        # без повторения, до тех пор пока все значения из множества In
        # не распределяться по выборкам
        if len(In)-In_end >= 0:
            sample.extend(In[In_start:In_end])
        else:                    
            # если элементов во множестве In недостаточно,
            # запоняем выборку "остатками" 
            sample.extend(In[In_start:])

            # остальные данные заполняем методом bootstrap
            # выполнем код пока не заполним выборку k значениями
            while len(sample) < k:
                # генерируем случайное число из диапазона от 0 до len(In)-1
                random_index = randint(0,len(In)-1)
                # добавляем значение из множества In с индексом random_index
                # в список index_list
                sample.append(In[random_index])

        # после того как мы набрали значения в выборку отправлем ее в samples_list
        samples_list.append(sample)
        # переходим к следующим данным в множестве In
        In_start+=k
        In_end+=k

    return samples_list

### <span style="color:RoyalBlue">функция my_train_test_split</span>

In [9]:
def my_train_test_split(X,y,random_state=42,train_size=0.8,):
    # если разбиение без стратификации

    # зададим число элементов в выборке train
    len_train = round(len(y)*train_size)
    # формируем множество натуральных чисел от 0 до max
    list_random_index = list(range(len(y)))
    # нарушим порядок в множестве
    list_random_index = shuffle(list_random_index,random_state=random_state)
    # формируем список индексов под train выборку
    train_samples = list_random_index[:len_train]
    # формируем список индексов под test выборку
    test_samples = list_random_index[len_train:]
    # выполнем код пока не заполним выборку k значениями
   
    X_train = X.iloc[train_samples]
    y_train = y.iloc[train_samples]
    X_test = X.iloc[test_samples]
    y_test = y.iloc[test_samples]

    return X_train, y_train, X_test, y_test

### <span style="color:RoyalBlue">функция class_1_percent_samples</span>

In [10]:
# функция class_1_percent_samples

# Назначение: для генерации индексов сбалансированных выборок

# Внешние переменные функции: 
#           1. data_target - массив из id и значений класса
#           2. class_1_percent - процент класса 1 в результирующей выборке
#           3. random_state - параметр для обеспечения воспроизваодимости функции
     

# Результат работы функции: 
# 1. samples_list - список со сблансированными выбороками

# обьявлем функцию
def class_1_percent_samples(data_target,class_1_percent,random_state = None):
    # приведем данные к нужной форме
    data_target = pd.DataFrame(data=np.array(data_target),columns =['id','flag'])
    
    # разделим клиентов  по признаку flag
    flag_0 = data_target[data_target['flag']==0].reset_index(drop=True)
    flag_1 = data_target[data_target['flag']==1].reset_index(drop=True)

    # определим класс большинства
    if flag_1.shape[0] > flag_0.shape[0]:
        majority_class = flag_1
        minority_class = flag_0
        # расчитаем необходимую величину выборки majority_class
        majority_class_size = round(minority_class.shape[0]*(class_1_percent)/(1-class_1_percent))
        # с помощью функции generate_samples сформируем выборку для majority_class
        samples_majority_class= generate_samples(majority_class.shape[0]-1,1,majority_class_size,random_state=random_state)
    else:
        majority_class = flag_0
        minority_class = flag_1
        # расчитаем необходимую величину выборки majority_class
        majority_class_size = round(minority_class.shape[0]*(1-class_1_percent)/(class_1_percent))
        # с помощью функции generate_samples сформируем выборку для majority_class
        samples_majority_class= generate_samples(majority_class.shape[0]-1,1,majority_class_size,random_state=random_state)
    
    # сформируем список выбороки с заданным процентом класс 1
    samples_list_id = minority_class['id'].values.tolist()+majority_class['id'].iloc[samples_majority_class[0]].tolist()

    return samples_list_id

# <span style="color:DeepSkyBlue">Процесс машинного обучения (ML-Machine Learning)</span>

Постановка задачи в рамках Machine Learning:
1. Для решения задачи построем блендинг моделей. 

2. В качестве базовых и метамоделей рассмотрим следующие классические модели классификации:
    - linear_model.LogisticRegression (Логистическая регрессия);
    - RandomForestClassifier (Деревья решений);
    - HistGradientBoostingClassifier (Градиентный бустинг).

3. В результате, преобразования данных было получено два пространства признаков (torow и stat признаки),  
состоящих из 6 подпространств:
    - date features;
    - late payments features; 
    - credit features;
    - relative features;
    - payments features;
    - service features.

4. На первом этапе построения потроения блендинга, сфокусируем обучение базовых моделей,   
на каждом подпространстве в отдельности друго от друга.  

5. На втором этапе построения блендинга, обучим несколько групп метамоделей.   
Первая группа метамоделей в качестве метапризнаков использует предсказания базовых моделей,    
обученных на пространстве признаков torow.  
Вторая группа метамоделей в качестве метапризнаков использует предсказания базовых моделей,    
обученных на пространстве признаков stat.

6. На третьем этапе построения блендинга метамодель обучится на метапризнаках пространства 
torow и stat.

<center> <img src = "img\Blending.jpg" alt="drawing" style="width:1400px;">

## <span style="color:DodgerBlue">Первый этап построения блендинга моделей</span>

### <span style="color:RoyalBlue">Построение модели на сбалансированных данных подпространства date torow</span>

#### <span style="color:MediumBlue">Построение модели Logistic Regression</span>

##### <span style="color:MediumSlateBlue">Формирование данных для обучения</span>

Анализ исходных данных, в частности target, показал что представленные данные   
имееют перекос: 96% клиентов у которых не случился дефолт (flag = 0),    
против 4 % - для которых произошел дефолт (flag = 1).  
С помощью функции class_1_percent_samples, сформируем сбаланисрованную выборку  
для обучения моделей.
За основу сбалансировных данных возьмем данные клиентов с дефолтом  
и к ним будем добирать необходимое количество клиентов до сбалансированности. 


Функция class_1_percent_samples принемает две переменные:
- target_data - массив с id и целевой переменной
- class_1_percent - процент класса 1 в результирующем массиве

In [11]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'date'
count_features = dict_spaces[feature_space]

In [12]:
# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

In [ ]:
# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)
y_train_pd.head(4)

id  flag
id                    
1825800  1825800     0
2166483  2166483     0
2534345  2534345     0
1803283  1803283     0

In [ ]:
# взглянем на сблансиорованность данных в y_train
y_train_pd['flag'].value_counts(normalize=True)
# flag
# 0    0.964242
# 1    0.035758
# Name: proportion, dtype: float64

flag
0    0.964242
1    0.035758
Name: proportion, dtype: float64

In [ ]:
# сбалансируем данные в y_train_pd
list_c1_percent_id = class_1_percent_samples(y_train_pd,0.5)
# list_c1_percent_features - список 'id' из y_train_pd соотвествующих  
# заданному проценту класса 1
len(list_c1_percent_id)
# 45860

45860

In [ ]:
# проверим сбалансированность полученного y_train
y_train_pd.loc[list_c1_percent_id]['flag'].value_counts(normalize=True)
# flag
# 1    0.5
# 0    0.5
# Name: proportion, dtype: float64

flag
1    0.5
0    0.5
Name: proportion, dtype: float64

*transform_data_torow*, показываеются последние N операций клиента.  
В данных в *date_torow*, собраны последние 25 операций клиентов.

Предварительный анализ показывает, что медиальное значение количества клиентских  
операций равно 7. Поэтому, для начала, будем показывать моделе $n_{last} = 7$   
последних клиентских операций.

Для извлечения из *transform_data_torow_25* необходимого количества последних клиенских  
операций ($n_{last}$) используем функцию features_from_transform_data_torow.

Функция features_from_transform_data_torow примает следующие аргументы:
- $n_{last} = 7$ - необходимое количество последних клиентских операций; 
- $n_{groups} = 8$ - количество признаков в $date$ $features$;
- $N_{last} = 25$ - количество $n_{last}$ операций, показанных в transform_data_torow_25


In [17]:
# с помощью функции features_from_transform_data_torow извлечем  
# из данных transform_data_torow_25
# признаки сооствествующие 7 последним клиенским операциям
list_n_last_features = features_from_transform_data_torow(7,count_features,25)

In [18]:
# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']
# сформируем данные для проверики модели
X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

In [19]:
# посмотрим на структуру данных в X_train_balanced
X_train_balanced.head(2)

f1  f2  f3  f4  f5  f6  f7  f8  f9  f10  ...  f191  f192  f193  f194  \
id                                                ...                           
2335465  12   9   2   2   3   3   4  18  18   18  ...     0     0     0     0   
390270   19  19   7  13  16  16   0   0   0    0  ...     0     0     0     0   

         f195  f196  f197  f198  f199  f200  
id                                           
2335465     0     0     0     0     0     0  
390270      0     0     0     0     0     0  

[2 rows x 200 columns]

In [ ]:
# посмотрим на структуру данных в y_train_balanced
y_train_balanced.head(2)
# id
# 2335465    1
# 390270     1
# Name: flag, dtype: int64

id
2335465    1
390270     1
Name: flag, dtype: int64

In [ ]:
# проверим что выборки действительно совпадают по id
X_train_balanced.index.to_list() == y_train_balanced.index.to_list()
# True

True

##### <span style="color:MediumSlateBlue">Baseline обучение модели LogisticRegression</span>

In [ ]:
# обучаем модель логистической регрессии
logistic_regression = linear_model.LogisticRegression(random_state=42, max_iter=10000)
logistic_regression.fit(np.array(X_train_balanced)[:,list_n_last_features],np.array(y_train_balanced))

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_LR_pred_proba = logistic_regression.predict_proba(X_train[:,list_n_last_features])[:,1]
y_valid_LR_pred_proba = logistic_regression.predict_proba(X_valid[:,list_n_last_features])[:,1]

# Делаем предсказание для валидационной выборки
y_valid_LR_pred = logistic_regression.predict(X_valid[:,list_n_last_features])

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_LR_pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_LR_pred_proba),3))

print('Основные метрики на тестовом наборе:')
print(metrics.classification_report(y_valid,y_valid_LR_pred))

# ROC AUC на обучающем наборе 0.581
# ROC AUC на валидационном наборе 0.577
# Основные метрики на тестовом наборе:
#               precision    recall  f1-score   support

#            0       0.97      0.54      0.69     68747
#            1       0.04      0.57      0.08      2503

#     accuracy                           0.54     71250
#    macro avg       0.51      0.56      0.39     71250
# weighted avg       0.94      0.54      0.67     71250

<span style="color:Blue">

Выводы:
Качество модели чуть лучше случайного угадывания.

##### <span style="color:MediumSlateBlue">Анализ влияния scaler преобразования на качество и скорость схождения модели</span>

In [ ]:
# формируем список из необходимых scaler
scalers = [MinMaxScaler(),RobustScaler() ,StandardScaler()]

# сформируем списко для заполнения данными результатов анализа
scalers_data = []

# установим ограничение на время обучения модели в 600 секунд (10 минут)
time_out = 600

for scaler in scalers:
        # для того чтобы следить за выполнением цикла введем индикатор
        print('current scaler: ', scaler)

         # сформируем список для заполнения данными текушего scaler
        current_scaler_data = [scaler]
        
        # выполним scaler преобразование
        X_train_s_balanced = scaler.fit_transform(np.array(X_train_balanced)[:,list_n_last_features])
        X_train_s = scaler.transform(X_train[:,list_n_last_features])
        X_valid_s = scaler.transform(X_valid[:,list_n_last_features])

        try:
                # для модуля func_time_out упакуем обучение модели в функцию try_func
                def try_func():
                        logistic_regression = linear_model.LogisticRegression(random_state=42, max_iter=10000)
                        return logistic_regression.fit(X_train_s_balanced,y_train_balanced)
                    
                # фиксируем время начала
                start_time = time.time()
                
                # запускаем обучение модели с ограничением по времени
                logistic_regression = func_timeout.func_timeout(time_out, try_func)
                
                # фиксируем время окончания обучения
                end_time = time.time()
                
                # запишем время обучения модели
                current_scaler_data.append(round(end_time-start_time))

                # Делаем предсказание для обучающей и валидационной выборки
                y_valid_lr_pred = logistic_regression.predict(X_valid_s)
                
                # для метрик ROC AUC делаем предсказание модели для обучающей и валидационной выборки  
                # в виде вероятности принадлежности к классу 1 
                y_train_lr_pred_proba = logistic_regression.predict_proba(X_train_s)[:,1]
                y_valid_lr_pred_proba = logistic_regression.predict_proba(X_valid_s)[:,1]

                #Считаем метрики ROC AUC yна обуающем и валидационном наборе и добавляем их в спискок
                current_scaler_data.append(round(metrics.roc_auc_score(y_train, y_train_lr_pred_proba),3))
                current_scaler_data.append(round(metrics.roc_auc_score(y_valid, y_valid_lr_pred_proba),3))

                #Считаем метрики для класса 0 на валидационном наборе и добавляем их в список
                current_scaler_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))
                current_scaler_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))


                #Считаем метрики для класса 1 на валидационном набопе и добавляем их в список
                current_scaler_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))
                current_scaler_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))

                # добавляем полученные данные в список scalers_data
                scalers_data.append(current_scaler_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                scaler_pd =pd.DataFrame(
                        columns=['scaler','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = scalers_data)
                # сохраняем dataframe
                scaler_pd.to_csv('data_recovery/scaler_pd.csv',index=False)
               
                # очистим output от прошедшей итерации
                clear_output()

        except func_timeout.FunctionTimedOut:
                # если время обучения привышает лимит
                # запишем в current_scaler_data соотвествующую данные
                current_scaler_data = [scaler,'>30m',0,0,0,0,0,0]
                # добавляем полученные данные в список scalers_data
                scalers_data.append(current_scaler_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                scaler_pd =pd.DataFrame(
                        columns=['scaler','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = scalers_data)
                # сохраняем dataframe
                scaler_pd.to_csv('data_recovery/scaler_pd.csv',index=False)
                
                # очистим output от прошедшей итерации
                clear_output()
                # переходим к следующему scaler
                pass
# очистим output
clear_output()

# сформируем данные соотвествующие лучщему ROC AUC на валидацинном наборе
best_roc_valid_data = scaler_pd[scaler_pd['roc_valid']==scaler_pd['roc_valid'].max()]

# выведем лучший результат на валидационном наборе
print('result:')
print('best scaler on valid:',best_roc_valid_data.iloc[0]['scaler'])
print('ROC AUC on train:', best_roc_valid_data.iloc[0]['roc_train'])
print('ROC AUC on valid:', best_roc_valid_data.iloc[0]['roc_valid'])
print('Time fit for best scaler:', best_roc_valid_data.iloc[0]['time_fit'],' seconds')

# выведем полученный dataframe
scaler_pd

# result:
# best scaler on valid: MinMaxScaler()
# ROC AUC on train: 0.581
# ROC AUC on valid: 0.577
# Time fit for best scaler: 0  seconds

<div>
<style scoped>
    .dataframe tbody tr th:only-of-type {
        vertical-align: middle;
    }

    .dataframe tbody tr th {
        vertical-align: top;
    }

    .dataframe thead th {
        text-align: right;
    }
</style>
<table border="1" class="dataframe">
  <thead>
    <tr style="text-align: right;">
      <th></th>
      <th>scaler</th>
      <th>time_fit</th>
      <th>roc_train</th>
      <th>roc_valid</th>
      <th>recall_0</th>
      <th>precision_0</th>
      <th>recall_1</th>
      <th>precision_1</th>
    </tr>
  </thead>
  <tbody>
    <tr>
      <th>0</th>
      <td>MinMaxScaler()</td>
      <td>0</td>
      <td>0.581</td>
      <td>0.577</td>
      <td>0.54</td>
      <td>0.972</td>
      <td>0.574</td>
      <td>0.043</td>
    </tr>
    <tr>
      <th>1</th>
      <td>RobustScaler()</td>
      <td>0</td>
      <td>0.581</td>
      <td>0.577</td>
      <td>0.54</td>
      <td>0.972</td>
      <td>0.574</td>
      <td>0.043</td>
    </tr>
    <tr>
      <th>2</th>
      <td>StandardScaler()</td>
      <td>0</td>
      <td>0.581</td>
      <td>0.577</td>
      <td>0.54</td>
      <td>0.972</td>
      <td>0.573</td>
      <td>0.043</td>
    </tr>
  </tbody>
</table>
</div>

<span style="color:Blue">

Выводы: $scaler$ преобразование ни как не повлияло на качество модели.



##### <span style="color:MediumSlateBlue"> Анализ влияния solver оптимизатора на качество и скорость обучения модели</span>

Проверим качество и скорость сходимости модели при разных solver  
Проверку осуществим через цикл  
Чтобы модель не сходилась бесконечно с помощью модуля func_timeout  
поставим ограничение времени схождения в 10 минут

In [24]:
# подготовим данные для обучения модели

# обьявим scaler
scaler = StandardScaler()
# выполним scaler преобразование
X_train_s_balanced = scaler.fit_transform(np.array(X_train_balanced)[:,list_n_last_features])
X_train_s = scaler.transform(X_train[:,list_n_last_features])
X_valid_s = scaler.transform(X_valid[:,list_n_last_features])

# time: 10s

In [ ]:
# Зададим список solvers
solvers_list = ['lbfgs', 'liblinear', 'newton-cg', 'newton-cholesky', 'sag', 'saga']

# сформируем список для заполнения
solvers_data = []

# установим ограничение на время обучения модели в 300 секунд (5 минут)
time_out = 300

for solver in solvers_list:
        # для того чтобы следить за выполнением цикла введем индикатор
        print('current solver: ', solver)

         # сформируем список для заполнения данными текушего solver
        current_solver_data = [solver]
        
        try:
                # для модуля func_time_out упакуем обучение модели в функцию try_func
                def try_func():
                        logistic_regression = linear_model.LogisticRegression(solver= solver,
                                                                  random_state=42, 
                                                                  max_iter=10000)
                        return logistic_regression.fit(X_train_s_balanced,y_train_balanced)
                    
                # фиксируем время начала
                start_time = time.time()
                
                # запускаем обучение модели с ограничением по времени
                logistic_regression = func_timeout.func_timeout(time_out, try_func)
                
                # фиксируем время окончания обучения
                end_time = time.time()
                
                # запишем время обучения модели
                current_solver_data.append(round(end_time-start_time))

                # Делаем предсказание для обучающей и валидационной выборки
                y_valid_lr_pred = logistic_regression.predict(X_valid_s)
                
                # для метрик ROC AUC делаем предсказание модели для обучающей и валидационной выборки  
                # в виде вероятности принадлежности к классу 1 
                y_train_lr_pred_proba = logistic_regression.predict_proba(X_train_s)[:,1]
                y_valid_lr_pred_proba = logistic_regression.predict_proba(X_valid_s)[:,1]

                #Считаем метрики ROC AUC yна обуающем и валидационном наборе и добавляем их в спискок
                current_solver_data.append(round(metrics.roc_auc_score(y_train, y_train_lr_pred_proba),3))
                current_solver_data.append(round(metrics.roc_auc_score(y_valid, y_valid_lr_pred_proba),3))

                #Считаем метрики для класса 0 на валидационном наборе и добавляем их в список
                current_solver_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))
                current_solver_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))


                #Считаем метрики для класса 1 на валидационном набопе и добавляем их в список
                current_solver_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))
                current_solver_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))

                # запишем данные полученные на одной итерации
                solvers_data.append(current_solver_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                solvers_pd =pd.DataFrame(
                        columns=['solver','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = solvers_data)
                # сохраняем dataframe
                solvers_pd.to_csv('data_recovery/solvers_pd.csv',index=False)
               
                # очистим output от прошедшей итерации
                clear_output()

        except func_timeout.FunctionTimedOut:
                # если время обучения привышает лимит
                # запишем в current_solver_data соотвествующую данные
                current_solver_data = [solver,'>10m',0,0,0,0,0,0]
                # добавляем полученные данные в список solvers_data
                solvers_data.append(current_solver_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                solvers_pd =pd.DataFrame(
                        columns=['solver','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = solvers_data)
                # сохраняем dataframe
                solvers_pd.to_csv('data_recovery/solvers_pd.csv',index=False)
                
                # очистим output от прошедшей итерации
                clear_output()
                # переходим к следующему solver
                pass
# очистим output
clear_output()

# сформируем данные соотвествующие лучщему ROC AUC на валидацинном наборе
best_roc_valid_data = solvers_pd[solvers_pd['roc_valid']==solvers_pd['roc_valid'].max()]

# выведем лучший результат на валидационном наборе
print('result:')
print('best solver on valid:',best_roc_valid_data.iloc[0]['solver'])
print('ROC AUC on train:', best_roc_valid_data.iloc[0]['roc_train'])
print('ROC AUC on valid:', best_roc_valid_data.iloc[0]['roc_valid'])
print('Time fit for best solver:', best_roc_valid_data.iloc[0]['time_fit'],' seconds')

# выведем полученный dataframe
solvers_pd

# result:
# best solver on valid: lbfgs
# ROC AUC on train: 0.581
# ROC AUC on valid: 0.577
# Time fit for best solver: 0  seconds

<div>
<style scoped>
    .dataframe tbody tr th:only-of-type {
        vertical-align: middle;
    }

    .dataframe tbody tr th {
        vertical-align: top;
    }

    .dataframe thead th {
        text-align: right;
    }
</style>
<table border="1" class="dataframe">
  <thead>
    <tr style="text-align: right;">
      <th></th>
      <th>solver</th>
      <th>time_fit</th>
      <th>roc_train</th>
      <th>roc_valid</th>
      <th>recall_0</th>
      <th>precision_0</th>
      <th>recall_1</th>
      <th>precision_1</th>
    </tr>
  </thead>
  <tbody>
    <tr>
      <th>0</th>
      <td>lbfgs</td>
      <td>0</td>
      <td>0.581</td>
      <td>0.577</td>
      <td>0.54</td>
      <td>0.972</td>
      <td>0.573</td>
      <td>0.043</td>
    </tr>
    <tr>
      <th>1</th>
      <td>liblinear</td>
      <td>0</td>
      <td>0.581</td>
      <td>0.577</td>
      <td>0.54</td>
      <td>0.972</td>
      <td>0.573</td>
      <td>0.043</td>
    </tr>
    <tr>
      <th>2</th>
      <td>newton-cg</td>
      <td>0</td>
      <td>0.581</td>
      <td>0.577</td>
      <td>0.54</td>
      <td>0.972</td>
      <td>0.573</td>
      <td>0.043</td>
    </tr>
    <tr>
      <th>3</th>
      <td>newton-cholesky</td>
      <td>0</td>
      <td>0.581</td>
      <td>0.577</td>
      <td>0.54</td>
      <td>0.972</td>
      <td>0.573</td>
      <td>0.043</td>
    </tr>
    <tr>
      <th>4</th>
      <td>sag</td>
      <td>1</td>
      <td>0.581</td>
      <td>0.577</td>
      <td>0.54</td>
      <td>0.972</td>
      <td>0.573</td>
      <td>0.043</td>
    </tr>
    <tr>
      <th>5</th>
      <td>saga</td>
      <td>0</td>
      <td>0.581</td>
      <td>0.577</td>
      <td>0.54</td>
      <td>0.972</td>
      <td>0.573</td>
      <td>0.043</td>
    </tr>
  </tbody>
</table>
</div>

<span style="color:Blue">

Вывод: Выбор $solver$ оптимизатора не влияет на качество модели.

##### <span style="color:MediumSlateBlue">Подбор гиперпараметров модели</span>

In [1407]:
# для выбора sceler преобразвания на понадобится словарь
dict_scalers ={
    'MinMaxScaler':MinMaxScaler(),
    'RobustScaler':RobustScaler(),
    'StandardScaler':StandardScaler(),
}
# определим пространство признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'date'
count_features = dict_spaces[feature_space]

# настроим оптимизацию гипер параметров
def optuna_lg(trial):
  # задаем пространства поиска гиперпараметров
  C = trial.suggest_float('C',0.01,1)
  solver = trial.suggest_categorical('solver', ['lbfgs', 'liblinear', 'newton-cg', 'newton-cholesky'])
  class_0_weight = trial.suggest_float('class_0_weight',0.4,1)
  class_1_weight = trial.suggest_float('class_1_weight',0.01,0.5)
  n_last = trial.suggest_int('n_last', 10, 25,step = 1)
  class_1_percent = trial.suggest_float('class_1_percent',0.01,1)
  scaler = trial.suggest_categorical('scaler', ['MinMaxScaler', 'RobustScaler','StandardScaler'])
  random_state = trial.suggest_int('random_state', 1, 1000000)

  # создаем модель
  optuna_log_reg = linear_model.LogisticRegression(
      solver=solver,
      C=C,
      class_weight={0:class_0_weight,1:class_1_weight},
      random_state=random_state,
      max_iter=10000)

  # с помощью функции features_from_transform_data_torow извлечем  
  # из данных transform_data_torow
  # признаки сооствествующие n_last последним клиенским операциям
  list_n_last_features = features_from_transform_data_torow(n_last,count_features,25)

  # обьявим scaler
  scaler = dict_scalers[scaler]

  # загружаем обучующие наборы
  X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
  y_train_pd = pd.read_csv('target/target_train.csv')

  # поготовим данные y_train_pd к работе с функцией class_1_percent_samples
  y_train_pd.set_index('id',drop=False,inplace=True)

  # подготовим данные для обучения модели
  # с помощью функции class_1_percent_samples зададим долю 
  # класса 1
  list_c1_percent_id = class_1_percent_samples(y_train_pd,class_1_percent,random_state=random_state)[:1000000]

  # сформируем данные для обучения базовой модели
  X_train_s_balanced = scaler.fit_transform(np.array(X_train_pd.loc[list_c1_percent_id])[:,list_n_last_features])
  y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

  # освободим память от "тяжелых" и ненужных файлов
  del X_train_pd, y_train_pd
  gc.collect()

  # я не воспользовался параметром timeout метода optimize потому, что  
  # optimize отставливает поиск параметров, если время обучения 
  # превышает timeout. Мне нужно чтобы поиск параметров продолжился.
  try:
    # для модуля func_time_out упакуем обучение модели в функцию try_func
    def try_func():
            return optuna_log_reg.fit(X_train_s_balanced, y_train_balanced)
    # обучаем модель с ограничением по времени 10 минут (600 секунд)
    optuna_log_reg = func_timeout.func_timeout(600, try_func)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train_s_balanced,y_train_balanced
    gc.collect()

    # подгружаем данные для тестирования
    X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()[:,list_n_last_features]
    y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
    X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()[:,list_n_last_features]
    y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

    # сформируем данные для проверки модели
    X_train_s = scaler.transform(X_train)
    X_valid_s = scaler.transform(X_valid)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train, X_valid
    gc.collect()

    # делаем предсказание на обучающем и валидационном наборе и считаем метрики
    roc_train = metrics.roc_auc_score(y_train, optuna_log_reg.predict_proba(X_train_s)[:,1])
    roc_valid = metrics.roc_auc_score(y_valid, optuna_log_reg.predict_proba(X_valid_s)[:,1])
    f1_score = metrics.f1_score(y_valid, optuna_log_reg.predict(X_valid_s))
    recall_1 = metrics.recall_score(y_valid, optuna_log_reg.predict(X_valid_s),average=None,zero_division=0)[1]
    precision_1 = metrics.precision_score(y_valid, optuna_log_reg.predict(X_valid_s),average=None,zero_division=0)[1]

    del X_train_s, X_valid_s, y_train, y_valid
    gc.collect()

  except func_timeout.FunctionTimedOut:
    # освободим память от "тяжелых" и ненужных файлов
    del X_train_s_balanced, y_train_balanced
    gc.collect()

    # обьявим метрики пустыми значениями
    roc_train = 0
    roc_valid = 0
    f1_score = 0
    recall_1 = 0
    precision_1 = 0
    pass

  return roc_train, roc_valid, f1_score, recall_1, precision_1

In [1408]:
# cоздаем объект исследования
# чтобы модель не переобучалась минимизируем roc_train 
# и максимизируем roc_valid
optuna_study_lg = optuna.create_study(study_name='LogisticRegression_'+feature_space+'_torow', 
                               directions=['maximize','maximize','maximize','maximize','maximize'], 
                               sampler=optuna.samplers.TPESampler(),
                               pruner='Hyperband',
                               storage='sqlite:///optuna_studies.db',
                               load_if_exists=True)
# на случай удаления 
# optuna.delete_study(study_name='LogisticRegression_'+feature_space+'_torow', storage='sqlite:///optuna_studies.db')

[I 2025-04-19 11:53:03,663] Using an existing study with name 'LogisticRegression_date_torow' instead of creating a new one.


In [ ]:
# ищем лучшую комбинацию гиперпараметров n_trials раз
optuna_study_lg.optimize(optuna_lg, n_trials=300)

In [1409]:
# из полученного результат соврмируем Data Frame
optuna_study_lg_pd = optuna_study_lg.trials_dataframe().dropna()
# переименуем столбы
optuna_study_lg_pd.rename(columns={
    'values_0': 'roc_train',
    'values_1': 'roc_valid',
    'values_2': 'f1_score',
    'values_3': 'recall_1',
    'values_4': 'precision_1'
},inplace=True)
# Выделим время потраченное на обучение модели
optuna_study_lg_pd.head(5)

number  roc_train  roc_valid  f1_score  recall_1  precision_1  \
0       0   0.585156   0.580831  0.000000  0.000000     0.000000   
1       1   0.575883   0.571258  0.067882  1.000000     0.035133   
2       2   0.494216   0.488417  0.067875  1.000000     0.035130   
3       3   0.588762   0.580936  0.000000  0.000000     0.000000   
4       4   0.574669   0.568678  0.070770  0.901318     0.036831   

              datetime_start          datetime_complete  \
0 2025-04-16 22:30:22.301366 2025-04-16 22:30:24.359872   
1 2025-04-16 22:30:24.366007 2025-04-16 22:30:26.061171   
2 2025-04-16 22:30:26.068443 2025-04-16 22:30:28.004159   
3 2025-04-16 22:30:28.010672 2025-04-16 22:30:32.571757   
4 2025-04-16 22:30:32.576553 2025-04-16 22:30:34.618155   

                duration  params_C  params_class_0_weight  \
0 0 days 00:00:02.058506  0.065408               0.924282   
1 0 days 00:00:01.695164  0.953829               0.786990   
2 0 days 00:00:01.935716  0.474446               0.938904   
3 0 days 00:00:04.561085  0.924273               0.568126   
4 0 days 00:00:02.041602  0.983989               0.509317   

   params_class_1_percent  params_class_1_weight  params_n_last  \
0                0.356860               0.034031           12.0   
1                0.888322               0.487496           12.0   
2                0.997258               0.234451           19.0   
3                0.056315               0.188176           24.0   
4                0.876853               0.111337           20.0   

   params_random_state   params_scaler    params_solver     state  
0             657775.0    RobustScaler  newton-cholesky  COMPLETE  
1             803577.0    MinMaxScaler        newton-cg  COMPLETE  
2             203330.0    MinMaxScaler        liblinear  COMPLETE  
3             873286.0  StandardScaler        newton-cg  COMPLETE  
4             468438.0    RobustScaler        newton-cg  COMPLETE

In [1410]:
# покаждем статистику обучения
print('Максимальное значение метрики ROC AUC на валидационном наборе:',round(optuna_study_lg_pd['roc_valid'].max(),3))
print('Среднее значение метрики ROC AUC на валидационном наборе:',round(optuna_study_lg_pd['roc_valid'].mean(),3))
print('Максимальное значение метрики f1_score на валидационном наборе:',round(optuna_study_lg_pd['f1_score'].max(),3))
print('Среднее значение метрики f1_score на валидационном наборе:',round(optuna_study_lg_pd['f1_score'].mean(),3))
print('Максимальное значение метрики recall_1 на валидационном наборе:',round(optuna_study_lg_pd['recall_1'].max(),3))
print('Среднее значение метрики recall_1 на валидационном наборе:',round(optuna_study_lg_pd['recall_1'].mean(),3))
print('Максимальное значение метрики precision_1 на валидационном наборе:',round(optuna_study_lg_pd['precision_1'].max(),3))
print('Среднее значение метрики precision_1 на валидационном наборе:',round(optuna_study_lg_pd['precision_1'].mean(),3))

Максимальное значение метрики ROC AUC на валидационном наборе: 0.582
Среднее значение метрики ROC AUC на валидационном наборе: 0.577
Максимальное значение метрики f1_score на валидационном наборе: 0.091
Среднее значение метрики f1_score на валидационном наборе: 0.059
Максимальное значение метрики recall_1 на валидационном наборе: 1.0
Среднее значение метрики recall_1 на валидационном наборе: 0.396
Максимальное значение метрики precision_1 на валидационном наборе: 0.2
Среднее значение метрики precision_1 на валидационном наборе: 0.043


In [1415]:
# Визуализируем метрики полученные при optuna оптимизации
fig = px.scatter(
    data_frame=optuna_study_lg_pd[
                                (optuna_study_lg_pd['roc_valid']>0.99*optuna_study_lg_pd['roc_valid'].max())& 
                                (optuna_study_lg_pd['f1_score']>0.99*optuna_study_lg_pd['f1_score'].max())],
    x='number', #ось абсцисс
    y=['roc_train','roc_valid','recall_1','precision_1','f1_score'], #ось ординат
)
fig.update_layout(
    title ={
        'text':'Зависимость качества модели от trials optuna', # Имя рабочей плоскости
        'font':{'size':35,'family':"Times New Roman"}, # размер и стиль написания имени рабочей плоскости
        'x':0.5, # Смешение имени по оси "x" на половину рабочей плоскости
        },
    height =800,# Высота рабочей плоскости
    width = 1350, # Ширина рабочей плоскости
    bargap=0.2, # Добавил расстояния между столбами гистограммы
    xaxis_title='trials optuna',
    yaxis_title='Величина метрики')
fig.update_xaxes(showspikes=True)
fig.update_yaxes(showspikes=True)

fig.show()

<span style="color:Blue">

Вывод:  

Их всех выбираем точку $number =91$.   
В этой точке одно из самых больших значений $ROC AUC$.  
Посмотрим каким значениям гиперпараметров соотвествует выбранная точка.

In [1418]:
# определим номер лучшге варианта
best_optuna_number = 91

# сформируем словарь лучших гипирпарметров RandomForestClassifier
best_param_lr_torow = {
    'C' : round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_C'].iloc[0],3),
    'class_weight' : {0:round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_class_0_weight'].iloc[0],3),
                      1:round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_class_1_weight'].iloc[0],3)},
    }
# создадим перменные
best_n_last = int(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_n_last'].iloc[0])
best_scaler = optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_scaler'].iloc[0]
best_class_1_percent = optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_class_1_percent'].iloc[0]
best_random_state = int(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_random_state'].iloc[0])
# Выведем принятые наилучшие праметры
print('best C:',best_param_lr_torow['C'])
print('best class 0 weight:',best_param_lr_torow['class_weight'][0])
print('best class 1 weight:',best_param_lr_torow['class_weight'][1])

print('best class 1 percent:',round(best_class_1_percent,3))
print('best scaler:',best_scaler)
print('best n_last:',round(best_n_last,3))
print('best best random state:',best_random_state)
print('time for best train:',round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['duration'].iloc[0].seconds/60),'minutes')

print()
print('ROC AUC на обучающем наборе:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['roc_train'].iloc[0],3))
print('ROC AUC на валидационном наборе:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['roc_valid'].iloc[0],3))
print('precision класса 1:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['precision_1'].iloc[0],3))
print('recall класса 1:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['recall_1'].iloc[0],3))

best C: 0.092
best class 0 weight: 0.445
best class 1 weight: 0.456
best class 1 percent: 0.431
best scaler: StandardScaler
best n_last: 12
best best random state: 634700
time for best train: 0 minutes

ROC AUC на обучающем наборе: 0.585
ROC AUC на валидационном наборе: 0.581
precision класса 1: 0.054
recall класса 1: 0.283


##### <span style="color:MediumSlateBlue">Обучение модели с лучшими параметрами</span>

In [1419]:
# для выбора sceler преобразвания на понадобится словарь
dict_scalers ={
    'MinMaxScaler':MinMaxScaler(),
    'RobustScaler':RobustScaler(),
    'StandardScaler':StandardScaler(),
}

# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'date'
count_features = dict_spaces[feature_space]

# с помощью функции features_from_transform_data_torow извлечем  
# из данных transform_data_torow_25
# признаки сооствествующие n_last последним клиенским операциям
list_n_last_features = features_from_transform_data_torow(best_n_last,count_features,25)

# обьявим scaler
scaler = dict_scalers[best_scaler]

# загружаем обучующие наборы
X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)

# подготовим данные для обучения модели
# с помощью функции class_1_percent_samples зададим долю 
# класса 1
list_c1_percent_id = class_1_percent_samples(y_train_pd,best_class_1_percent,random_state=best_random_state)[:1000000]

# сформируем данные для обучения базовой модели
X_train_s_balanced = scaler.fit_transform(np.array(X_train_pd.loc[list_c1_percent_id])[:,list_n_last_features])
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

# освободим память от "тяжелых" и ненужных файлов
del X_train_pd, y_train_pd
gc.collect()


# обучаем модель LogisticRegression с наилучшеми параметрами
logistic_regression = linear_model.LogisticRegression(
        **best_param_lr_torow,
        random_state=best_random_state,
        max_iter=10000)
logistic_regression.fit(X_train_s_balanced,y_train_balanced)

# удаляем крупные файлы чтобы высвободить память 
del X_train_s_balanced,y_train_balanced
gc.collect()

# подгружаем данные для тестирования
X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()[:,list_n_last_features]
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()[:,list_n_last_features]
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()
    
# сформируем данные для проверки модели
X_train_s = scaler.transform(X_train)
X_valid_s = scaler.transform(X_valid)

# удаляем крупные файлы чтобы высвободить память 
del X_train, X_valid
gc.collect()

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_lr_pred_proba = logistic_regression.predict_proba(X_train_s)[:,1]
y_valid_lr_pred_proba = logistic_regression.predict_proba(X_valid_s)[:,1]

# Делаем предсказание для валидационной выборки
y_valid_lr_pred = logistic_regression.predict(X_valid_s)

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_lr_pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_lr_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_lr_pred,zero_division=0))

# time: 2m 40s

ROC AUC на обучающем наборе 0.585
ROC AUC на валидационном наборе 0.581
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.97      0.82      0.89     68747
           1       0.05      0.28      0.09      2503

    accuracy                           0.80     71250
   macro avg       0.51      0.55      0.49     71250
weighted avg       0.94      0.80      0.86     71250



<span style="color:Blue">
Вывод:  

Модель $LogisticRegression$, обученная на сбалансированных данных   
$transform$ $data$ $torow$ имеет низкую предсказательную способность.

Подбор гиперпараметров модели не смог значительно улучшить ее качество.

#### <span style="color:MediumBlue">Построение модели Random Forest Classifier</span>

##### <span style="color:MediumSlateBlue">Формирование данных для обучения</span>

Анализ исходных данных, в частности target, показал что представленные данные   
имееют перекос: 96% клиентов у которых не случился дефолт (flag = 0),    
против 4 % - для которых произошел дефолт (flag = 1).  
С помощью функции class_1_percent_samples, сформируем сбаланисрованную выборку  
для обучения моделей.
За основу сбалансировных данных возьмем данные клиентов с дефолтом  
и к ним будем добирать необходимое количество клиентов до сбалансированности. 


Функция class_1_percent_samples принемает две переменные:
- target_data - массив с id и целевой переменной
- class_1_percent - процент класса 1 в результирующем массиве

In [1420]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'date'
count_features = dict_spaces[feature_space]

In [1421]:
# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

In [1422]:
# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)
y_train_pd.head(4)

id  flag
id                    
1825800  1825800     0
2166483  2166483     0
2534345  2534345     0
1803283  1803283     0

In [1423]:
# взглянем на сблансиорованность данных в y_train
y_train_pd['flag'].value_counts(normalize=True)

flag
0    0.964242
1    0.035758
Name: proportion, dtype: float64

In [1424]:
# сбалансируем данные в y_train_pd
list_c1_percent_id = class_1_percent_samples(y_train_pd,0.5)
# list_c1_percent_features - список 'id' из y_train_pd соотвествующих  
# заданному проценту класса 1
len(list_c1_percent_id)

45860

In [1425]:
# проверим сбалансированность полученного y_train
y_train_pd.loc[list_c1_percent_id]['flag'].value_counts(normalize=True)

flag
1    0.5
0    0.5
Name: proportion, dtype: float64

*transform_data_torow*, показываеются последние N операций клиента.  
В данных в *date_torow*, собраны последние 25 операций клиентов.

Предварительный анализ показывает, что медиальное значение количества клиентских  
операций равно 7. Поэтому, для начала, будем показывать моделе $n_{last} = 7$   
последних клиентских операций.

Для извлечения из *transform_data_torow_25* необходимого количества последних клиенских  
операций ($n_{last}$) используем функцию features_from_transform_data_torow.

Функция features_from_transform_data_torow примает следующие аргументы:
- $n_{last} = 7$ - необходимое количество последних клиентских операций; 
- $n_{groups} = 8$ - количество признаков в $date$ $features$;
- $N_{last} = 25$ - количество $n_{last}$ операций, показанных в transform_data_torow_25


In [1426]:
# с помощью функции features_from_transform_data_torow извлечем  
# из данных transform_data_torow_25
# признаки сооствествующие 7 последним клиенским операциям
list_n_last_features = features_from_transform_data_torow(7,count_features,25)

In [1427]:
# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']
# сформируем данные для проверики модели
X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

In [1428]:
# посмотрим на структуру данных в X_train_balanced
X_train_balanced.head(2)

f1  f2  f3  f4  f5  f6  f7  f8  f9  f10  ...  f191  f192  f193  f194  \
id                                                ...                           
2335465  12   9   2   2   3   3   4  18  18   18  ...     0     0     0     0   
390270   19  19   7  13  16  16   0   0   0    0  ...     0     0     0     0   

         f195  f196  f197  f198  f199  f200  
id                                           
2335465     0     0     0     0     0     0  
390270      0     0     0     0     0     0  

[2 rows x 200 columns]

In [1429]:
# посмотрим на структуру данных в y_train_balanced
y_train_balanced.head(2)

id
2335465    1
390270     1
Name: flag, dtype: int64

In [1430]:
# проверим что выборки действительно совпадают по id
X_train_balanced.index.to_list() == y_train_balanced.index.to_list()

True

##### <span style="color:MediumSlateBlue">Baseline обучение модели RandomForestClassifier</span>

In [1431]:
# обучаем модель логистической регрессии
# чтобы модель пыталась найти связь во всех признаках
random_forest = RandomForestClassifier(random_state=42, n_jobs=-1)
random_forest.fit(np.array(X_train_balanced)[:,list_n_last_features],np.array(y_train_balanced))

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_rf__pred_proba = random_forest.predict_proba(X_train[:,list_n_last_features])[:,1]
y_valid_rf_pred_proba = random_forest.predict_proba(X_valid[:,list_n_last_features])[:,1]

# Делаем предсказание для валидационной выборки
y_valid_rf_pred = random_forest.predict(X_valid[:,list_n_last_features])

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_rf__pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_rf_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_rf_pred))

# time: 2m 5s

ROC AUC на обучающем наборе 0.974
ROC AUC на валидационном наборе 0.588
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.97      0.65      0.78     68747
           1       0.05      0.48      0.09      2503

    accuracy                           0.65     71250
   macro avg       0.51      0.56      0.43     71250
weighted avg       0.94      0.65      0.76     71250



<span style="color:Blue">

Выводы:

1. Модель подает признаки переобучения.
2. Качество модели по метрики $roc$ $valid$ чуть лучше, чем у модели   
$Logistic$ $Regression$.


##### <span style="color:MediumSlateBlue">Подбор гиперпараметров модели</span>

In [1432]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'date'
count_features = dict_spaces[feature_space]

# настроим оптимизацию гипер параметров
def optuna_rf(trial):
  # задаем пространства поиска гиперпараметров
  # задаем пространства поиска гиперпараметров
  n_estimators = trial.suggest_int('n_estimators', 50, 150,step = 5)
  criterion = trial.suggest_categorical('criterion',['gini', 'entropy', 'log_loss'])
  max_depth = trial.suggest_int('max_depth', 9, 20,step = 1)
  min_samples_split = trial.suggest_int('min_samples_split', 5, 15,step = 1)
  min_samples_leaf = trial.suggest_int('min_samples_leaf', 5, 25,step = 1)
  max_features = trial.suggest_float('max_features',0.1,1)
  max_samples = trial.suggest_float('max_samples',0.1,1)
  class_0_weight = trial.suggest_float('class_0_weight',0.2,0.6)
  class_1_weight = trial.suggest_float('class_1_weight',0.4,1)
  n_last = trial.suggest_int('n_last', 5, 25,step = 1)
  class_1_percent = trial.suggest_float('class_1_percent',0.2,0.6)
  random_state = trial.suggest_int('random_state', 1, 1000000)


  # создаем модель
  optuna_random_forest = RandomForestClassifier(
      n_estimators = n_estimators, 
      criterion = criterion,
      max_depth = max_depth,
      min_samples_split = min_samples_split,  
      min_samples_leaf = min_samples_leaf,
      max_features=max_features,
      max_samples=max_samples,
      class_weight={0:class_0_weight,1:class_1_weight},
      n_jobs=-1,
      random_state=random_state)

  # с помощью функции features_from_transform_data_torow извлечем  
  # из данных transform_data_torow
  # признаки сооствествующие n_last последним клиенским операциям
  list_n_last_features = features_from_transform_data_torow(n_last,count_features,25)

  # загружаем обучующие наборы
  X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
  y_train_pd = pd.read_csv('target/target_train.csv')

  # поготовим данные y_train_pd к работе с функцией class_1_percent_samples
  y_train_pd.set_index('id',drop=False,inplace=True)

  # подготовим данные для обучения модели
  # с помощью функции class_1_percent_samples зададим долю 
  # класса 1
  list_c1_percent_id = class_1_percent_samples(y_train_pd,class_1_percent,random_state=random_state)[:1000000]

  # сформируем данные для обучения базовой модели
  X_train_balanced = np.array(X_train_pd.loc[list_c1_percent_id])[:,list_n_last_features]
  y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

  # освободим память от "тяжелых" и ненужных файлов
  del X_train_pd, y_train_pd
  gc.collect()

  # я не воспользовался параметром timeout метода optimize потому, что  
  # optimize отставливает поиск параметров, если время обучения 
  # превышает timeout. Мне нужно чтобы поиск параметров продолжился.
  try:
    # для модуля func_time_out упакуем обучение модели в функцию try_func
    def try_func():
            return optuna_random_forest.fit(X_train_balanced,y_train_balanced)
    # обучаем модель с ограничением по времени 10 минут (600 секунд)
    optuna_random_forest = func_timeout.func_timeout(600, try_func)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train_balanced, y_train_balanced
    gc.collect()

    # подгружаем данные для тестирования
    X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()[:,list_n_last_features]
    y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
    X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()[:,list_n_last_features]
    y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

    # делаем предсказание на обучающем и валидационном наборе и считаем метрики
    roc_train = metrics.roc_auc_score(y_train, optuna_random_forest.predict_proba(X_train)[:,1])
    roc_valid = metrics.roc_auc_score(y_valid, optuna_random_forest.predict_proba(X_valid)[:,1])
    f1_score = metrics.f1_score(y_valid, optuna_random_forest.predict(X_valid))
    recall_1 = metrics.recall_score(y_valid, optuna_random_forest.predict(X_valid),average=None,zero_division=0)[1]
    precision_1 = metrics.precision_score(y_valid, optuna_random_forest.predict(X_valid),average=None,zero_division=0)[1]

    # удаляем крупные файлы чтобы высвободить память 
    del X_train, X_valid, y_train, y_valid 
    gc.collect()

  except func_timeout.FunctionTimedOut:
    # освободим память от "тяжелых" и ненужных файлов
    del X_train_balanced, y_train_balanced
    gc.collect()

    # обьявим метрики пустыми значениями
    roc_train = 0
    roc_valid = 0
    f1_score = 0
    recall_1 = 0
    precision_1 = 0
    pass

  return roc_train, roc_valid, f1_score, recall_1, precision_1

In [1433]:
# так как Random Forest склонен к переобучению 
# попробуем направить optimize в сторону уменьшения roc_train
# cоздаем объект исследования
optuna_study_rf = optuna.create_study(study_name='RandomForestClassifier_'+feature_space+'_torow', 
                               directions=['minimize','maximize','maximize','maximize','maximize'], 
                               sampler=optuna.samplers.TPESampler(),
                               pruner='Hyperband',
                               storage='sqlite:///optuna_studies.db',
                               load_if_exists=True)
# на случай удаления 
# optuna.delete_study(study_name='RandomForestClassifier_'+feature_space+'_torow', storage='sqlite:///optuna_studies.db')

[I 2025-04-19 11:56:11,895] Using an existing study with name 'RandomForestClassifier_date_torow' instead of creating a new one.


In [60]:
# ищем лучшую комбинацию гиперпараметров n_trials раз
optuna_study_rf.optimize(optuna_rf, n_trials=300)

[I 2025-04-17 08:27:13,446] Trial 300 finished with values: [0.7147586165348679, 0.6204920278916932, 0.0939003957078179, 0.5261685976827807, 0.05155002348520432] and parameters: {'n_estimators': 130, 'criterion': 'entropy', 'max_depth': 10, 'min_samples_split': 7, 'min_samples_leaf': 22, 'max_features': 0.8140099475865336, 'max_samples': 0.8692267879418314, 'class_0_weight': 0.2735456178455244, 'class_1_weight': 0.7757026755861152, 'n_last': 5, 'class_1_percent': 0.2730474860608997, 'random_state': 507790}.
[I 2025-04-17 08:27:26,520] Trial 301 finished with values: [0.7150633762929891, 0.6189082475983364, 0.09464558079794493, 0.4710347582900519, 0.05260809423943599] and parameters: {'n_estimators': 130, 'criterion': 'log_loss', 'max_depth': 10, 'min_samples_split': 8, 'min_samples_leaf': 22, 'max_features': 0.9869478839335802, 'max_samples': 0.5460687317050787, 'class_0_weight': 0.27327094210845704, 'class_1_weight': 0.7696005303555892, 'n_last': 7, 'class_1_percent': 0.27298265240147

In [1434]:
# из полученного результат соврмируем Data Frame
optuna_study_rf_pd = optuna_study_rf.trials_dataframe().dropna()
# переименуем столбы
optuna_study_rf_pd.rename(columns={
    'values_0': 'roc_train',
    'values_1': 'roc_valid',
    'values_2': 'f1_score',
    'values_3': 'recall_1',
    'values_4': 'precision_1'
},inplace=True)
optuna_study_rf_pd.sort_values(by='precision_1').drop(['datetime_start','datetime_complete','duration'],axis=1)

number  roc_train  roc_valid  f1_score  recall_1  precision_1  \
35       35   0.698704   0.608574  0.067855  0.999600     0.035120   
319     319   0.639965   0.611560  0.067876  1.000000     0.035130   
90       90   0.688097   0.613549  0.067876  1.000000     0.035130   
305     305   0.678113   0.616256  0.067878  0.999600     0.035132   
140     140   0.642815   0.608499  0.067922  0.999600     0.035155   
..      ...        ...        ...       ...       ...          ...   
106     106   0.833275   0.619415  0.005477  0.002797     0.132075   
492     492   0.689019   0.614609  0.017183  0.009189     0.132184   
520     520   0.708116   0.614129  0.014378  0.007591     0.135714   
10       10   0.683171   0.610665  0.052292  0.032361     0.136134   
189     189   0.695279   0.612376  0.045939  0.027567     0.137725   

     params_class_0_weight  params_class_1_percent  params_class_1_weight  \
35                0.325041                0.599089               0.526356   
319               0.288083                0.517601               0.817832   
90                0.390308                0.575775               0.920527   
305               0.261755                0.467088               0.809737   
140               0.494122                0.562375               0.864030   
..                     ...                     ...                    ...   
106               0.594318                0.229883               0.430477   
492               0.439928                0.223496               0.464473   
520               0.548631                0.276511               0.405100   
10                0.575194                0.209638               0.766080   
189               0.576082                0.200175               0.789783   

    params_criterion  params_max_depth  params_max_features  \
35           entropy                17             0.116665   
319         log_loss                 9             0.999992   
90              gini                 9             0.774467   
305          entropy                10             0.582057   
140          entropy                 9             0.839327   
..               ...               ...                  ...   
106          entropy                18             0.177464   
492         log_loss                 9             0.734330   
520          entropy                10             0.753639   
10              gini                12             0.477256   
189          entropy                12             0.926263   

     params_max_samples  params_min_samples_leaf  params_min_samples_split  \
35             0.519446                       19                        12   
319            0.114836                       23                         5   
90             0.844483                       18                         6   
305            0.381491                       20                         5   
140            0.138724                       24                         5   
..                  ...                      ...                       ...   
106            0.814594                       18                         7   
492            0.759346                       23                         7   
520            0.791233                       22                         6   
10             0.154922                       23                         7   
189            0.153640                       23                         5   

     params_n_estimators  params_n_last  params_random_state     state  
35                    75             19               355123  COMPLETE  
319                  150              5               920675  COMPLETE  
90                   145              7               470313  COMPLETE  
305                  130              5               570204  COMPLETE  
140                  145             12               456947  COMPLETE  
..                   ...            ...                  ...       ...  
106                  150          

In [1435]:
# покаждем статистику обучения
print('Максимальное значение метрики ROC AUC на валидационном наборе:',round(optuna_study_rf_pd['roc_valid'].max(),3))
print('Среднее значение метрики ROC AUC на валидационном наборе:',round(optuna_study_rf_pd['roc_valid'].mean(),3))
print('Максимальное значение метрики f1_score на валидационном наборе:',round(optuna_study_rf_pd['f1_score'].max(),3))
print('Среднее значение метрики f1_score на валидационном наборе:',round(optuna_study_rf_pd['f1_score'].mean(),3))
print('Максимальное значение метрики recall_1 на валидационном наборе:',round(optuna_study_rf_pd['recall_1'].max(),3))
print('Среднее значение метрики recall_1 на валидационном наборе:',round(optuna_study_rf_pd['recall_1'].mean(),3))
print('Максимальное значение метрики precision_1 на валидационном наборе:',round(optuna_study_rf_pd['precision_1'].max(),3))
print('Среднее значение метрики precision_1 на валидационном наборе:',round(optuna_study_rf_pd['precision_1'].mean(),3))

Максимальное значение метрики ROC AUC на валидационном наборе: 0.623
Среднее значение метрики ROC AUC на валидационном наборе: 0.614
Максимальное значение метрики f1_score на валидационном наборе: 0.114
Среднее значение метрики f1_score на валидационном наборе: 0.093
Максимальное значение метрики recall_1 на валидационном наборе: 1.0
Среднее значение метрики recall_1 на валидационном наборе: 0.398
Максимальное значение метрики precision_1 на валидационном наборе: 0.138
Среднее значение метрики precision_1 на валидационном наборе: 0.067


In [1440]:
# Построим зависимость метрик качества модели от number

fig = px.scatter(
    data_frame=optuna_study_rf_pd[(optuna_study_rf_pd['roc_valid']>=0.99*optuna_study_rf_pd['roc_valid'].max())&
                                  (optuna_study_rf_pd['f1_score']>=0.99*optuna_study_rf_pd['f1_score'].max())],
    x='number', #ось абсцисс
    y=['roc_valid','roc_train','precision_1','recall_1','f1_score'], #ось ординат
)
fig.update_layout(
    title ={
        'text':'Зависимость качества модели от trials optuna', # Имя рабочей плоскости
        'font':{'size':35,'family':"Times New Roman"}, # размер и стиль написания имени рабочей плоскости
        'x':0.5, # Смешение имени по оси "x" на половину рабочей плоскости
        },
    height =800,# Высота рабочей плоскости
    width = 1350, # Ширина рабочей плоскости
    bargap=0.2, # Добавил расстояния между столбами гистограммы
    xaxis_title='trials optuna',
    yaxis_title='Величина параметра')
fig.update_xaxes(showspikes=True)
fig.update_yaxes(showspikes=True)

fig.show()

<span style="color:Blue">

Вывод:  

Их всех выбираем точку $number =532$.   
В этой точке оптимальные значения метрик $recall_1$ и $precision_1$, а  
также относительно высокая метрика $ROC AUC$.   
Посмотрим каким значениям гиперпараметров соотвествует выбраннаяточка.

In [1441]:
# определим номер лучшге варианта
best_optuna_number = 532

# сформируем словарь лучших гипирпарметров RandomForestClassifier
best_param_rf = {
    'n_estimators' : int(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_n_estimators'].iloc[0]),
    'criterion': optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_criterion'].iloc[0],
    'max_depth' : optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_max_depth'].iloc[0],
    'min_samples_split': optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_min_samples_split'].iloc[0],
    'min_samples_leaf' : optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_min_samples_leaf'].iloc[0],
    'max_features': optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_max_features'].iloc[0],
    'max_samples' : optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_max_samples'].iloc[0],
    'class_weight' : {0:optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_class_0_weight'].iloc[0],
                      1:optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_class_1_weight'].iloc[0]}
    }
# определим перменные для лучших значений параметров
best_n_last = optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_n_last'].iloc[0]
best_class_1_percent = optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_class_1_percent'].iloc[0]
best_random_state = optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_random_state'].iloc[0]


# Выведем принятые наилучшие праметры
print('best n estimators:',best_param_rf['n_estimators'])
print('best criterion:',best_param_rf['criterion'])
print('best max depth:',best_param_rf['max_depth'])
print('best min samples split:',best_param_rf['min_samples_split'])
print('best min samples leaf:',best_param_rf['min_samples_leaf'])
print('best max features(%):',round(best_param_rf['max_features'],3))
print('best max samples(%):',round(best_param_rf['max_samples'],3))
print('best class 0 weight:',round(best_param_rf['class_weight'][0],3))
print('best class 1 weight:',round(best_param_rf['class_weight'][1],3))

print('best class 1 percent:',round(best_class_1_percent,3))
print('best n last:',best_n_last)
print('best random state:',best_random_state)
print('time for best train:',round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['duration'].iloc[0].seconds/60),'minutes')

print()
print('ROC AUC на обучающем наборе:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['roc_train'].iloc[0],3))
print('ROC AUC на валидационном наборе:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['roc_valid'].iloc[0],3))
print('precision класса 1:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['precision_1'].iloc[0],3))
print('recall класса 1:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['recall_1'].iloc[0],3))

best n estimators: 120
best criterion: entropy
best max depth: 15
best min samples split: 6
best min samples leaf: 22
best max features(%): 0.798
best max samples(%): 0.799
best class 0 weight: 0.44
best class 1 weight: 0.618
best class 1 percent: 0.304
best n last: 5
best random state: 551450
time for best train: 0 minutes

ROC AUC на обучающем наборе: 0.794
ROC AUC на валидационном наборе: 0.618
precision класса 1: 0.085
recall класса 1: 0.171


##### <span style="color:MediumSlateBlue">Обучение модели с лучшими параметрами</span>

In [1442]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'date'
count_features = dict_spaces[feature_space]

# с помощью функции features_from_transform_data_torow извлечем  
# из данных transform_data_torow
# признаки сооствествующие n_last последним клиенским операциям
list_n_last_features = features_from_transform_data_torow(best_n_last,count_features,25)

# загружаем обучующие наборы
X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)

# подготовим данные для обучения модели
# с помощью функции class_1_percent_samples зададим долю 
# класса 1
list_c1_percent_id = class_1_percent_samples(y_train_pd,best_class_1_percent,random_state=best_random_state)[:1000000]

# сформируем данные для обучения базовой модели
X_train_balanced = np.array(X_train_pd.loc[list_c1_percent_id])[:,list_n_last_features]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

# освободим память от "тяжелых" и ненужных файлов
del X_train_pd, y_train_pd
gc.collect()

# обучаем модель RandomForestClassifier с наилучшеми параметрами
random_forest = RandomForestClassifier(
        **best_param_rf,
        n_jobs=-1,
        random_state=best_random_state)
random_forest.fit(X_train_balanced, y_train_balanced)

# освободим память от "тяжелых" и ненужных файлов
del X_train_balanced, y_train_balanced
gc.collect()


# подгружаем данные для тестирования
X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()[:,list_n_last_features]
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()[:,list_n_last_features]
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_rf__pred_proba = random_forest.predict_proba(X_train)[:,1]
y_valid_rf_pred_proba = random_forest.predict_proba(X_valid)[:,1]

# Делаем предсказание для валидационной выборки
y_valid_rf_pred = random_forest.predict(X_valid)

# удаляем крупные файлы чтобы высвободить память 
del X_train, X_valid
gc.collect()

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_rf__pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_rf_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_rf_pred,zero_division=0))

# time: 2m 10s

ROC AUC на обучающем наборе 0.794
ROC AUC на валидационном наборе 0.618
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.97      0.93      0.95     68747
           1       0.08      0.17      0.11      2503

    accuracy                           0.91     71250
   macro avg       0.53      0.55      0.53     71250
weighted avg       0.94      0.91      0.92     71250



<span style="color:Blue">
Вывод:  

Модель $Random$ $Forest$ $Classifier$, обученная на сбалансированных данных   
$date$ $torow$, показывает лучшее качество по метрике $ROC AUC$,  
чем модель $Logistic$ $Regression$ $Classifier$, обученная на тех же данных.  
В остальном модель имеют похожую способность отделять класс 1 от класс 0.

#### <span style="color:MediumBlue">Построение модели Gradient Boosting Classifier</span>

##### <span style="color:MediumSlateBlue">Формирование данных для обучения</span>

Анализ исходных данных, в частности target, показал что представленные данные   
имееют перекос: 96% клиентов у которых не случился дефолт (flag = 0),    
против 4 % - для которых произошел дефолт (flag = 1).  
С помощью функции class_1_percent_samples, сформируем сбаланисрованную выборку  
для обучения моделей.
За основу сбалансировных данных возьмем данные клиентов с дефолтом  
и к ним будем добирать необходимое количество клиентов до сбалансированности. 


Функция class_1_percent_samples принемает две переменные:
- target_data - массив с id и целевой переменной
- class_1_percent - процент класса 1 в результирующем массиве

In [1443]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'date'
count_features = dict_spaces[feature_space]

In [1444]:
# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

In [1445]:
# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)
y_train_pd.head(4)

id  flag
id                    
1825800  1825800     0
2166483  2166483     0
2534345  2534345     0
1803283  1803283     0

In [1446]:
# взглянем на сблансиорованность данных в y_train
y_train_pd['flag'].value_counts(normalize=True)

flag
0    0.964242
1    0.035758
Name: proportion, dtype: float64

In [1447]:
# сбалансируем данные в y_train_pd
list_c1_percent_id = class_1_percent_samples(y_train_pd,0.5)
# list_c1_percent_features - список 'id' из y_train_pd соотвествующих  
# заданному проценту класса 1
len(list_c1_percent_id)

45860

In [1448]:
# проверим сбалансированность полученного y_train
y_train_pd.loc[list_c1_percent_id]['flag'].value_counts(normalize=True)

flag
1    0.5
0    0.5
Name: proportion, dtype: float64

*transform_data_torow*, показываеются последние N операций клиента.  
В данных в *date_torow*, собраны последние 25 операций клиентов.

Предварительный анализ показывает, что медиальное значение количества клиентских  
операций равно 7. Поэтому, для начала, будем показывать моделе $n_{last} = 7$   
последних клиентских операций.

Для извлечения из *transform_data_torow_25* необходимого количества последних клиенских  
операций ($n_{last}$) используем функцию features_from_transform_data_torow.

Функция features_from_transform_data_torow примает следующие аргументы:
- $n_{last} = 7$ - необходимое количество последних клиентских операций; 
- $n_{groups} = 8$ - количество признаков в $date$ $features$;
- $N_{last} = 25$ - количество $n_{last}$ операций, показанных в transform_data_torow_25


In [1449]:
# с помощью функции features_from_transform_data_torow извлечем  
# из данных transform_data_torow_25
# признаки сооствествующие 7 последним клиенским операциям
list_n_last_features = features_from_transform_data_torow(7,count_features,25)

In [1450]:
# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']
# сформируем данные для проверики модели
X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

In [1451]:
# посмотрим на структуру данных в X_train_balanced
X_train_balanced.head(2)

f1  f2  f3  f4  f5  f6  f7  f8  f9  f10  ...  f191  f192  f193  f194  \
id                                                ...                           
2335465  12   9   2   2   3   3   4  18  18   18  ...     0     0     0     0   
390270   19  19   7  13  16  16   0   0   0    0  ...     0     0     0     0   

         f195  f196  f197  f198  f199  f200  
id                                           
2335465     0     0     0     0     0     0  
390270      0     0     0     0     0     0  

[2 rows x 200 columns]

In [1452]:
# посмотрим на структуру данных в y_train_balanced
y_train_balanced.head(2)

id
2335465    1
390270     1
Name: flag, dtype: int64

In [1453]:
# проверим что выборки действительно совпадают по id
X_train_balanced.index.to_list() == y_train_balanced.index.to_list()

True

##### <span style="color:MediumSlateBlue">Baseline обучение модели Hist Gradient Boosting Classifier</span>

In [1454]:
# обучаем модель Gradient Boosting Classifier
gradient_boosting = HistGradientBoostingClassifier(random_state=42)
gradient_boosting.fit(np.array(X_train_balanced)[:,list_n_last_features],np.array(y_train_balanced))

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_rf__pred_proba = gradient_boosting.predict_proba(X_train[:,list_n_last_features])[:,1]
y_valid_rf_pred_proba = gradient_boosting.predict_proba(X_valid[:,list_n_last_features])[:,1]

# Делаем предсказание для валидационной выборки
y_valid_rf_pred = gradient_boosting.predict(X_valid[:,list_n_last_features])

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_rf__pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_rf_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_rf_pred))

# time: 

ROC AUC на обучающем наборе 0.66
ROC AUC на валидационном наборе 0.622
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.97      0.62      0.76     68747
           1       0.05      0.55      0.09      2503

    accuracy                           0.62     71250
   macro avg       0.51      0.59      0.43     71250
weighted avg       0.94      0.62      0.74     71250



<span style="color:Blue">

Выводы:

1. Качество модели по метрики $ROC AUC$ лучше, чем у предыдущих моделей.
2. В остальном, качество модели не изменилось.

##### <span style="color:MediumSlateBlue">Подбор гиперпараметров модели</span>

In [1455]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'date'
count_features = dict_spaces[feature_space]

# настроим оптимизацию гипер параметров
def optuna_hgbc(trial):
  # задаем пространства поиска гиперпараметров
  learning_rate = trial.suggest_float('learning_rate',0.2,0.6)
  max_iter = trial.suggest_int('max_iter', 50, 300,step = 1)
  max_leaf_nodes = trial.suggest_int('max_leaf_nodes', 2, 50,step = 1)
  max_depth = trial.suggest_int('max_depth', 1, 15,step = 1)
  min_samples_leaf = trial.suggest_int('min_samples_leaf', 1, 50,step = 1)
  max_features = trial.suggest_float('max_features',0.1,1)
  l2_regularization = trial.suggest_float('l2_regularization',0.01,1)
  class_0_weight = trial.suggest_float('class_0_weight',0.01,1)
  class_1_weight = trial.suggest_float('class_1_weight',0.01,1)
  n_last = trial.suggest_int('n_last', 5, 25,step = 1)
  class_1_percent = trial.suggest_float('class_1_percent',0.01,0.5)
  random_state = trial.suggest_int('random_state', 1, 1000000)


  # создаем модель
  optuna_gradient_boosting = HistGradientBoostingClassifier(
      learning_rate= learning_rate,
      max_iter = max_iter,
      max_leaf_nodes =max_leaf_nodes,
      max_depth = max_depth,
      min_samples_leaf = min_samples_leaf,
      max_features=max_features,
      l2_regularization = l2_regularization,
      class_weight={0:class_0_weight,1:class_1_weight},
      random_state=42)

  # с помощью функции features_from_transform_data_torow извлечем  
  # из данных transform_data_torow
  # признаки сооствествующие n_last последним клиенским операциям
  list_n_last_features = features_from_transform_data_torow(n_last,count_features,25)

  # загружаем обучующие наборы
  X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
  y_train_pd = pd.read_csv('target/target_train.csv')

  # поготовим данные y_train_pd к работе с функцией class_1_percent_samples
  y_train_pd.set_index('id',drop=False,inplace=True)

  # подготовим данные для обучения модели
  # с помощью функции class_1_percent_samples зададим долю класса 1
  list_c1_percent_id = class_1_percent_samples(y_train_pd,class_1_percent,random_state=random_state)[:1000000]

  # сформируем данные для обучения модели
  X_train_balanced = np.array(X_train_pd.loc[list_c1_percent_id])[:,list_n_last_features]
  y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

  # освободим память от "тяжелых" и ненужных файлов
  del X_train_pd, y_train_pd
  gc.collect()

  # я не воспользовался параметром timeout метода optimize потому, что  
  # optimize отставливает поиск параметров, если время обучения 
  # превышает timeout. Мне нужно чтобы поиск параметров продолжился.
  try:
    # для модуля func_time_out упакуем обучение модели в функцию try_func
    def try_func():
            return optuna_gradient_boosting.fit(X_train_balanced,y_train_balanced)
    # обучаем модель с ограничением по времени 10 минут (600 секунд)
    optuna_gradient_boosting = func_timeout.func_timeout(600, try_func)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train_balanced, y_train_balanced
    gc.collect()

    # подгружаем данные для тестирования
    X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()[:,list_n_last_features]
    y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
    X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()[:,list_n_last_features]
    y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

    # делаем предсказание на обучающем и валидационном наборе и считаем метрики
    roc_train = metrics.roc_auc_score(y_train, optuna_gradient_boosting.predict_proba(X_train)[:,1])
    roc_valid = metrics.roc_auc_score(y_valid, optuna_gradient_boosting.predict_proba(X_valid)[:,1])
    f1_score = metrics.f1_score(y_valid, optuna_gradient_boosting.predict(X_valid))
    recall_1 = metrics.recall_score(y_valid, optuna_gradient_boosting.predict(X_valid),average=None,zero_division=0)[1]
    precision_1 = metrics.precision_score(y_valid, optuna_gradient_boosting.predict(X_valid),average=None,zero_division=0)[1]

    # удаляем крупные файлы чтобы высвободить память 
    del X_train, X_valid, y_train, y_valid 
    gc.collect()

  except func_timeout.FunctionTimedOut:
    # освободим память от "тяжелых" и ненужных файлов
    del X_train_balanced, y_train_balanced
    gc.collect()

    # обьявим метрики пустыми значениями
    roc_train = 0
    roc_valid = 0
    f1_score = 0
    recall_1 = 0
    precision_1 = 0
    pass

  return roc_train, roc_valid, f1_score, recall_1, precision_1

In [1456]:
# cоздаем объект исследования
# чтобы модель не переобучалась минимизируем roc_train 
# и максимизируем roc_valid
optuna_study_hsbs = optuna.create_study(study_name='HistGradientBoostingClassifier_'+feature_space+'_torow', 
                               directions=['maximize','maximize','maximize','maximize','maximize'], 
                               sampler=optuna.samplers.TPESampler(),
                               pruner='Hyperband',
                               storage='sqlite:///optuna_studies.db',
                               load_if_exists=True)

# ну случай удаления обучения
# optuna.delete_study(study_name='HistGradientBoostingClassifier_'+feature_space+'_torow', storage='sqlite:///optuna_studies.db')

[I 2025-04-19 11:59:02,249] Using an existing study with name 'HistGradientBoostingClassifier_date_torow' instead of creating a new one.


In [92]:
# ищем лучшую комбинацию гиперпараметров n_trials раз
optuna_study_hsbs.optimize(optuna_hgbc, n_trials=300)

[I 2025-04-17 09:28:57,707] Trial 300 finished with values: [0.7071910784646855, 0.6312473935229896, 0.11121289849761817, 0.24250898921294448, 0.07215024367050993] and parameters: {'learning_rate': 0.2188429752886377, 'max_iter': 214, 'max_leaf_nodes': 46, 'max_depth': 5, 'min_samples_leaf': 14, 'max_features': 0.6454559928045788, 'l2_regularization': 0.7236729137413304, 'class_0_weight': 0.3056268840420504, 'class_1_weight': 0.984112222593508, 'n_last': 7, 'class_1_percent': 0.1654082484536172, 'random_state': 557475}.
[I 2025-04-17 09:29:06,863] Trial 301 finished with values: [0.7082811732882602, 0.6347793821719724, 0.10249139153331983, 0.10107870555333599, 0.10394412489728841] and parameters: {'learning_rate': 0.2001425029757014, 'max_iter': 223, 'max_leaf_nodes': 20, 'max_depth': 5, 'min_samples_leaf': 44, 'max_features': 0.7518545596275877, 'l2_regularization': 0.7025872131235211, 'class_0_weight': 0.3584339578374115, 'class_1_weight': 0.9983471575161484, 'n_last': 9, 'class_1_pe

In [1457]:
# из полученного результат соврмируем Data Frame
optuna_study_hsbs_pd = optuna_study_hsbs.trials_dataframe()
# переименуем столбы
optuna_study_hsbs_pd.rename(columns={
    'values_0': 'roc_train',
    'values_1': 'roc_valid',
    'values_2': 'f1_score',
    'values_3': 'recall_1',
    'values_4': 'precision_1'
},inplace=True)
# Выделим время потраченное на обучение модели
last_trail = optuna_study_hsbs_pd['number'].max()
optuna_study_hsbs_pd.tail(5)


number  roc_train  roc_valid  f1_score  recall_1  precision_1  \
595     595   0.702015   0.627585  0.112587  0.228526     0.074693   
596     596   0.691480   0.633316  0.092693  0.596484     0.050251   
597     597   0.673148   0.632791  0.012796  0.006792     0.110390   
598     598   0.703565   0.627597  0.077666  0.843388     0.040707   
599     599   0.714106   0.626786  0.111169  0.170196     0.082542   

                datetime_start          datetime_complete  \
595 2025-04-17 10:16:45.873236 2025-04-17 10:16:58.840913   
596 2025-04-17 10:16:58.847122 2025-04-17 10:17:10.978233   
597 2025-04-17 10:17:10.984455 2025-04-17 10:17:32.219188   
598 2025-04-17 10:17:32.224923 2025-04-17 10:17:45.027973   
599 2025-04-17 10:17:45.034168 2025-04-17 10:17:58.453180   

                  duration  params_class_0_weight  ...  \
595 0 days 00:00:12.967677               0.104082  ...   
596 0 days 00:00:12.131111               0.072225  ...   
597 0 days 00:00:21.234733               0.115384  ...   
598 0 days 00:00:12.803050               0.035309  ...   
599 0 days 00:00:13.419012               0.061805  ...   

     params_l2_regularization  params_learning_rate  params_max_depth  \
595                  0.787289              0.206156                 7   
596                  0.778874              0.250551                 4   
597                  0.498560              0.213494                 3   
598                  0.527920              0.226099                 5   
599                  0.702846              0.200287                11   

     params_max_features  params_max_iter  params_max_leaf_nodes  \
595             0.977234              240                     26   
596             0.665270              173                     49   
597             0.610843              177                     37   
598             0.544218              169                     46   
599             0.737382              297                     47   

     params_min_samples_leaf  params_n_last  params_random_state     state  
595                       44             13               723609  COMPLETE  
596                       27              7               713102  COMPLETE  
597                       42              9               676938  COMPLETE  
598                       17             10               140546  COMPLETE  
599                       41              9               640462  COMPLETE  

[5 rows x 22 columns]

In [1458]:
# покаждем статистику обучения
print('Максимальное значение метрики ROC AUC на валидационном наборе:',round(optuna_study_hsbs_pd['roc_valid'].max(),3))
print('Среднее значение метрики ROC AUC на валидационном наборе:',round(optuna_study_hsbs_pd['roc_valid'].mean(),3))
print('Максимальное значение метрики f1_score на валидационном наборе:',round(optuna_study_hsbs_pd['f1_score'].max(),3))
print('Среднее значение метрики f1_score на валидационном наборе:',round(optuna_study_hsbs_pd['f1_score'].mean(),3))
print('Максимальное значение метрики recall_1 на валидационном наборе:',round(optuna_study_hsbs_pd['recall_1'].max(),3))
print('Среднее значение метрики recall_1 на валидационном наборе:',round(optuna_study_hsbs_pd['recall_1'].mean(),3))
print('Максимальное значение метрики precision_1 на валидационном наборе:',round(optuna_study_hsbs_pd['precision_1'].max(),3))
print('Среднее значение метрики precision_1 на валидационном наборе:',round(optuna_study_hsbs_pd['precision_1'].mean(),3))

Максимальное значение метрики ROC AUC на валидационном наборе: 0.638
Среднее значение метрики ROC AUC на валидационном наборе: 0.626
Максимальное значение метрики f1_score на валидационном наборе: 0.116
Среднее значение метрики f1_score на валидационном наборе: 0.073
Максимальное значение метрики recall_1 на валидационном наборе: 1.0
Среднее значение метрики recall_1 на валидационном наборе: 0.39
Максимальное значение метрики precision_1 на валидационном наборе: 1.0
Среднее значение метрики precision_1 на валидационном наборе: 0.075


In [1466]:
# Построим зависимость метрик качества модели от number

fig = px.scatter(
    data_frame=optuna_study_hsbs_pd[(optuna_study_hsbs_pd['roc_valid']>0.95*optuna_study_hsbs_pd['roc_valid'].max())&
                                    (optuna_study_hsbs_pd['f1_score']>0.98*optuna_study_hsbs_pd['f1_score'].max())
                                     ],
    x='number', #ось абсцисс
    y=['roc_train','roc_valid','recall_1','precision_1','f1_score'], #ось ординат
)
fig.update_layout(
    title ={
        'text':'Зависимость precision от гиперпараметров модели', # Имя рабочей плоскости
        'font':{'size':35,'family':"Times New Roman"}, # размер и стиль написания имени рабочей плоскости
        'x':0.5, # Смешение имени по оси "x" на половину рабочей плоскости
        },
    height =800,# Высота рабочей плоскости
    width = 1350, # Ширина рабочей плоскости
    bargap=0.2, # Добавил расстояния между столбами гистограммы
    xaxis_title='Величина метрики precision_1',
    yaxis_title='Величина параметра')
fig.update_xaxes(showspikes=True)
fig.update_yaxes(showspikes=True)

fig.show()

<span style="color:Blue">

Вывод:  

Их всех выбираем точку $number =386$.   
В этой точке оптимальные значения метрик $recall_1$ и $precision_1$, а  
также относительно высокая метрика $ROC AUC$.   
Посмотрим каким значениям гиперпараметров соотвествует выбранная точка.

In [1468]:
# определим номер лучшге варианта
best_optuna_number = 386

# сформируем словарь лучших гипирпарметров RandomForestClassifier
best_param_rf = {
    'learning_rate' : optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_learning_rate'].iloc[0],
    'max_iter' : optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_max_iter'].iloc[0],
    'max_leaf_nodes' : optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_max_leaf_nodes'].iloc[0],
    'max_depth' : optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_max_depth'].iloc[0],
    'min_samples_leaf' : optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_min_samples_leaf'].iloc[0],
    'max_features' : optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_max_features'].iloc[0],
    'l2_regularization' : optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_l2_regularization'].iloc[0],
    'class_weight' : {0: optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_class_0_weight'].iloc[0],
                      1: optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_class_1_weight'].iloc[0],}
    }

# определим перменные для лучших значений параметров
best_n_last = optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_n_last'].iloc[0]
best_class_1_percent = optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_class_1_percent'].iloc[0]
best_random_state = optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_random_state'].iloc[0]


# Выведем принятые наилучшие праметры
print('best learning rate:',round(best_param_rf['learning_rate'],3))
print('best max iter:',best_param_rf['max_iter'])
print('best max leaf nodes:',best_param_rf['max_leaf_nodes'])
print('best max depth:',best_param_rf['max_depth'])
print('best min samples leaf:',best_param_rf['min_samples_leaf'])
print('best max features:',round(best_param_rf['max_features'],3))
print('best l2 regularization:',round(best_param_rf['l2_regularization'],3))
print('best class 0 weight:',round(best_param_rf['class_weight'][0],3))
print('best class 1 weight:',round(best_param_rf['class_weight'][1],3))

print('best class 1 percent:',round(best_class_1_percent,3))
print('best n last:',best_n_last)
print('best random state:',best_random_state)
print('time for best train:',round(optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['duration'].iloc[0].seconds/60),'minutes')

print()
print('ROC AUC на обучающем наборе:', round(optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['roc_train'].iloc[0],3))
print('ROC AUC на валидационном наборе:', round(optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['roc_valid'].iloc[0],3))
print('precision класса 1:', round(optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['precision_1'].iloc[0],3))
print('recall класса 1:', round(optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['recall_1'].iloc[0],3))

best learning rate: 0.22
best max iter: 256
best max leaf nodes: 25
best max depth: 6
best min samples leaf: 11
best max features: 0.892
best l2 regularization: 0.787
best class 0 weight: 0.078
best class 1 weight: 0.885
best class 1 percent: 0.049
best n last: 8
best random state: 118157
time for best train: 0 minutes

ROC AUC на обучающем наборе: 0.688
ROC AUC на валидационном наборе: 0.636
precision класса 1: 0.085
recall класса 1: 0.173


##### <span style="color:MediumSlateBlue">Обучение модели с лучшими параметрами</span>

In [1469]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'date'
count_features = dict_spaces[feature_space]

# с помощью функции features_from_transform_data_torow извлечем  
# из данных transform_data_torow
# признаки сооствествующие n_last последним клиенским операциям
list_n_last_features = features_from_transform_data_torow(best_n_last,count_features,25)

# загружаем обучующие наборы
X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)

# подготовим данные для обучения модели
# с помощью функции class_1_percent_samples зададим долю класса 1
list_c1_percent_id = class_1_percent_samples(y_train_pd,best_class_1_percent,random_state=best_random_state)[:1000000]

# сформируем данные для обучения модели
X_train_balanced = np.array(X_train_pd.loc[list_c1_percent_id])[:,list_n_last_features]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

# освободим память от "тяжелых" и ненужных файлов
del X_train_pd, y_train_pd
gc.collect()


# обучаем модель HistGradientBoostingClassifier с наилучшеми параметрами
gradient_boosting = HistGradientBoostingClassifier(
        **best_param_rf,
        random_state=42)
gradient_boosting.fit(X_train_balanced,y_train_balanced)

# освободим память от "тяжелых" и ненужных файлов
del X_train_balanced, y_train_balanced
gc.collect()

# подгружаем данные для тестирования
X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()[:,list_n_last_features]
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()[:,list_n_last_features]
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_gb__pred_proba = gradient_boosting.predict_proba(X_train)[:,1]
y_valid_gb_pred_proba = gradient_boosting.predict_proba(X_valid)[:,1]

# Делаем предсказание для валидационной выборки
y_valid_gb_pred = gradient_boosting.predict(X_valid)

# освободим память от "тяжелых" и ненужных файлов
del X_train, X_valid
gc.collect()

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_gb__pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_gb_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_gb_pred,zero_division=0))

# time: 2m 30s

ROC AUC на обучающем наборе 0.688
ROC AUC на валидационном наборе 0.636
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.97      0.93      0.95     68747
           1       0.08      0.17      0.11      2503

    accuracy                           0.91     71250
   macro avg       0.53      0.55      0.53     71250
weighted avg       0.94      0.91      0.92     71250



<span style="color:Blue">
Вывод:  

Модель $Hist$ $Gradient$ $Boosting$ $Classifier$, обученная на сбалансированных данных   
$transform$ $data$ $torow$, показывает лучшее качество по метрике $ROC AUC$,  
чем предыдущие модели, обученные на тех же данных.  
В остальном модель имеют похожую способность отделять класс 1 от класс 0.

### <span style="color:RoyalBlue">Построение модели на сбалансированных данных подпространства late torow</span>

#### <span style="color:MediumBlue">Построение модели Logistic Regression</span>

##### <span style="color:MediumSlateBlue">Формирование данных для обучения</span>

Анализ исходных данных, в частности target, показал что представленные данные   
имееют перекос: 96% клиентов у которых не случился дефолт (flag = 0),    
против 4 % - для которых произошел дефолт (flag = 1).  
С помощью функции class_1_percent_samples, сформируем сбаланисрованную выборку  
для обучения моделей.
За основу сбалансировных данных возьмем данные клиентов с дефолтом  
и к ним будем добирать необходимое количество клиентов до сбалансированности. 


Функция class_1_percent_samples принемает две переменные:
- target_data - массив с id и целевой переменной
- class_1_percent - процент класса 1 в результирующем массиве

In [1470]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'late'
count_features = dict_spaces[feature_space]

In [1471]:
# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

In [1472]:
# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)
y_train_pd.head(4)

id  flag
id                    
1825800  1825800     0
2166483  2166483     0
2534345  2534345     0
1803283  1803283     0

In [1473]:
# взглянем на сблансиорованность данных в y_train
y_train_pd['flag'].value_counts(normalize=True)

flag
0    0.964242
1    0.035758
Name: proportion, dtype: float64

In [1474]:
# сбалансируем данные в y_train_pd
list_c1_percent_id = class_1_percent_samples(y_train_pd,0.5)
# list_c1_percent_features - список 'id' из y_train_pd соотвествующих  
# заданному проценту класса 1
len(list_c1_percent_id)

45860

In [1475]:
# проверим сбалансированность полученного y_train
y_train_pd.loc[list_c1_percent_id]['flag'].value_counts(normalize=True)

flag
1    0.5
0    0.5
Name: proportion, dtype: float64

*transform_data_torow*, показываеются последние N операций клиента.  
В данных в *date_torow*, собраны последние 25 операций клиентов.

Предварительный анализ показывает, что медиальное значение количества клиентских  
операций равно 7. Поэтому, для начала, будем показывать моделе $n_{last} = 7$   
последних клиентских операций.

Для извлечения из *transform_data_torow_25* необходимого количества последних клиенских  
операций ($n_{last}$) используем функцию features_from_transform_data_torow.

Функция features_from_transform_data_torow примает следующие аргументы:
- $n_{last} = 7$ - необходимое количество последних клиентских операций; 
- $n_{groups} = 8$ - количество признаков в $date$ $features$;
- $N_{last} = 25$ - количество $n_{last}$ операций, показанных в transform_data_torow_25


In [1476]:
# с помощью функции features_from_transform_data_torow извлечем  
# из данных transform_data_torow_25
# признаки сооствествующие 7 последним клиенским операциям
list_n_last_features = features_from_transform_data_torow(7,count_features,25)

In [1477]:
# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']
# сформируем данные для проверики модели
X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

In [1478]:
# посмотрим на структуру данных в X_train_balanced
X_train_balanced.head(2)

f1  f2  f3  f4  f5  f6  f7  f8  f9  f10  ...  f291  f292  f293  f294  \
id                                                ...                           
2335465   6   6   6   6   6   6   6   6   6    6  ...     2     2     0     0   
390270    6   6   6   6   6   6   0   0   0    0  ...     0     0     0     0   

         f295  f296  f297  f298  f299  f300  
id                                           
2335465     0     0     0     0     0     0  
390270      0     0     0     0     0     0  

[2 rows x 300 columns]

In [1479]:
# посмотрим на структуру данных в y_train_balanced
y_train_balanced.head(2)

id
2335465    1
390270     1
Name: flag, dtype: int64

In [1480]:
# проверим что выборки действительно совпадают по id
X_train_balanced.index.to_list() == y_train_balanced.index.to_list()

True

##### <span style="color:MediumSlateBlue">Baseline обучение модели LogisticRegression</span>

In [1290]:
# обучаем модель логистической регрессии
logistic_regression = linear_model.LogisticRegression(random_state=42, max_iter=10000)
logistic_regression.fit(np.array(X_train_balanced)[:,list_n_last_features],np.array(y_train_balanced))

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_LR_pred_proba = logistic_regression.predict_proba(X_train[:,list_n_last_features])[:,1]
y_valid_LR_pred_proba = logistic_regression.predict_proba(X_valid[:,list_n_last_features])[:,1]

# Делаем предсказание для валидационной выборки
y_valid_LR_pred = logistic_regression.predict(X_valid[:,list_n_last_features])

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_LR_pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_LR_pred_proba),3))

print('Основные метрики на тестовом наборе:')
print(metrics.classification_report(y_valid,y_valid_LR_pred))

# time: 1m 12s

ROC AUC на обучающем наборе 0.613
ROC AUC на валидационном наборе 0.618
Основные метрики на тестовом наборе:
              precision    recall  f1-score   support

           0       0.97      0.69      0.81     68747
           1       0.05      0.49      0.10      2503

    accuracy                           0.68     71250
   macro avg       0.51      0.59      0.45     71250
weighted avg       0.94      0.68      0.78     71250



##### <span style="color:MediumSlateBlue">Анализ влияния scaler преобразования на качество и скорость схождения модели</span>

In [122]:
# формируем список из необходимых scaler
scalers = [MinMaxScaler(),RobustScaler() ,StandardScaler()]

# сформируем списко для заполнения данными результатов анализа
scalers_data = []

# установим ограничение на время обучения модели в 600 секунд (10 минут)
time_out = 600

for scaler in scalers:
        # для того чтобы следить за выполнением цикла введем индикатор
        print('current scaler: ', scaler)

         # сформируем список для заполнения данными текушего scaler
        current_scaler_data = [scaler]
        
        # выполним scaler преобразование
        X_train_s_balanced = scaler.fit_transform(np.array(X_train_balanced)[:,list_n_last_features])
        X_train_s = scaler.transform(X_train[:,list_n_last_features])
        X_valid_s = scaler.transform(X_valid[:,list_n_last_features])

        try:
                # для модуля func_time_out упакуем обучение модели в функцию try_func
                def try_func():
                        logistic_regression = linear_model.LogisticRegression(random_state=42, max_iter=10000)
                        return logistic_regression.fit(X_train_s_balanced,y_train_balanced)
                    
                # фиксируем время начала
                start_time = time.time()
                
                # запускаем обучение модели с ограничением по времени
                logistic_regression = func_timeout.func_timeout(time_out, try_func)
                
                # фиксируем время окончания обучения
                end_time = time.time()
                
                # запишем время обучения модели
                current_scaler_data.append(round(end_time-start_time))

                # Делаем предсказание для обучающей и валидационной выборки
                y_valid_lr_pred = logistic_regression.predict(X_valid_s)
                
                # для метрик ROC AUC делаем предсказание модели для обучающей и валидационной выборки  
                # в виде вероятности принадлежности к классу 1 
                y_train_lr_pred_proba = logistic_regression.predict_proba(X_train_s)[:,1]
                y_valid_lr_pred_proba = logistic_regression.predict_proba(X_valid_s)[:,1]

                #Считаем метрики ROC AUC yна обуающем и валидационном наборе и добавляем их в спискок
                current_scaler_data.append(round(metrics.roc_auc_score(y_train, y_train_lr_pred_proba),3))
                current_scaler_data.append(round(metrics.roc_auc_score(y_valid, y_valid_lr_pred_proba),3))

                #Считаем метрики для класса 0 на валидационном наборе и добавляем их в список
                current_scaler_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))
                current_scaler_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))


                #Считаем метрики для класса 1 на валидационном набопе и добавляем их в список
                current_scaler_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))
                current_scaler_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))

                # добавляем полученные данные в список scalers_data
                scalers_data.append(current_scaler_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                scaler_pd =pd.DataFrame(
                        columns=['scaler','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = scalers_data)
                # сохраняем dataframe
                scaler_pd.to_csv('data_recovery/scaler_pd.csv',index=False)
               
                # очистим output от прошедшей итерации
                clear_output()

        except func_timeout.FunctionTimedOut:
                # если время обучения привышает лимит
                # запишем в current_scaler_data соотвествующую данные
                current_scaler_data = [scaler,'>30m',0,0,0,0,0,0]
                # добавляем полученные данные в список scalers_data
                scalers_data.append(current_scaler_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                scaler_pd =pd.DataFrame(
                        columns=['scaler','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = scalers_data)
                # сохраняем dataframe
                scaler_pd.to_csv('data_recovery/scaler_pd.csv',index=False)
                
                # очистим output от прошедшей итерации
                clear_output()
                # переходим к следующему scaler
                pass
# очистим output
clear_output()

# сформируем данные соотвествующие лучщему ROC AUC на валидацинном наборе
best_roc_valid_data = scaler_pd[scaler_pd['roc_valid']==scaler_pd['roc_valid'].max()]

# выведем лучший результат на валидационном наборе
print('result:')
print('best scaler on valid:',best_roc_valid_data.iloc[0]['scaler'])
print('ROC AUC on train:', best_roc_valid_data.iloc[0]['roc_train'])
print('ROC AUC on valid:', best_roc_valid_data.iloc[0]['roc_valid'])
print('Time fit for best scaler:', best_roc_valid_data.iloc[0]['time_fit'],' seconds')

# выведем полученный dataframe
scaler_pd

# time: 

result:
best scaler on valid: MinMaxScaler()
ROC AUC on train: 0.613
ROC AUC on valid: 0.617
Time fit for best scaler: 0  seconds


scaler  time_fit  roc_train  roc_valid  recall_0  precision_0  \
0    MinMaxScaler()         0      0.613      0.617     0.691        0.974   
1    RobustScaler()         0      0.613      0.617     0.691        0.974   
2  StandardScaler()         0      0.613      0.617     0.690        0.974   

   recall_1  precision_1  
0     0.491        0.055  
1     0.493        0.055  
2     0.493        0.055

##### <span style="color:MediumSlateBlue"> Анализ влияния solver оптимизатора на качество и скорость обучения модели</span>

Проверим качество и скорость сходимости модели при разных solver  
Проверку осуществим через цикл  
Чтобы модель не сходилась бесконечно с помощью модуля func_timeout  
поставим ограничение времени схождения в 10 минут

In [123]:
# подготовим данные для обучения модели

# обьявим scaler
scaler = StandardScaler()
# выполним scaler преобразование
X_train_s_balanced = scaler.fit_transform(np.array(X_train_balanced)[:,list_n_last_features])
X_train_s = scaler.transform(X_train[:,list_n_last_features])
X_valid_s = scaler.transform(X_valid[:,list_n_last_features])

# time: 10s

In [124]:
# Зададим список solvers
solvers_list = ['lbfgs', 'liblinear', 'newton-cg', 'newton-cholesky', 'sag', 'saga']

# сформируем список для заполнения
solvers_data = []

# установим ограничение на время обучения модели в 300 секунд (5 минут)
time_out = 300

for solver in solvers_list:
        # для того чтобы следить за выполнением цикла введем индикатор
        print('current solver: ', solver)

         # сформируем список для заполнения данными текушего solver
        current_solver_data = [solver]
        
        try:
                # для модуля func_time_out упакуем обучение модели в функцию try_func
                def try_func():
                        logistic_regression = linear_model.LogisticRegression(solver= solver,
                                                                  random_state=42, 
                                                                  max_iter=10000)
                        return logistic_regression.fit(X_train_s_balanced,y_train_balanced)
                    
                # фиксируем время начала
                start_time = time.time()
                
                # запускаем обучение модели с ограничением по времени
                logistic_regression = func_timeout.func_timeout(time_out, try_func)
                
                # фиксируем время окончания обучения
                end_time = time.time()
                
                # запишем время обучения модели
                current_solver_data.append(round(end_time-start_time))

                # Делаем предсказание для обучающей и валидационной выборки
                y_valid_lr_pred = logistic_regression.predict(X_valid_s)
                
                # для метрик ROC AUC делаем предсказание модели для обучающей и валидационной выборки  
                # в виде вероятности принадлежности к классу 1 
                y_train_lr_pred_proba = logistic_regression.predict_proba(X_train_s)[:,1]
                y_valid_lr_pred_proba = logistic_regression.predict_proba(X_valid_s)[:,1]

                #Считаем метрики ROC AUC yна обуающем и валидационном наборе и добавляем их в спискок
                current_solver_data.append(round(metrics.roc_auc_score(y_train, y_train_lr_pred_proba),3))
                current_solver_data.append(round(metrics.roc_auc_score(y_valid, y_valid_lr_pred_proba),3))

                #Считаем метрики для класса 0 на валидационном наборе и добавляем их в список
                current_solver_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))
                current_solver_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))


                #Считаем метрики для класса 1 на валидационном набопе и добавляем их в список
                current_solver_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))
                current_solver_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))

                # запишем данные полученные на одной итерации
                solvers_data.append(current_solver_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                solvers_pd =pd.DataFrame(
                        columns=['solver','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = solvers_data)
                # сохраняем dataframe
                solvers_pd.to_csv('data_recovery/solvers_pd.csv',index=False)
               
                # очистим output от прошедшей итерации
                clear_output()

        except func_timeout.FunctionTimedOut:
                # если время обучения привышает лимит
                # запишем в current_solver_data соотвествующую данные
                current_solver_data = [solver,'>10m',0,0,0,0,0,0]
                # добавляем полученные данные в список solvers_data
                solvers_data.append(current_solver_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                solvers_pd =pd.DataFrame(
                        columns=['solver','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = solvers_data)
                # сохраняем dataframe
                solvers_pd.to_csv('data_recovery/solvers_pd.csv',index=False)
                
                # очистим output от прошедшей итерации
                clear_output()
                # переходим к следующему solver
                pass
# очистим output
clear_output()

# сформируем данные соотвествующие лучщему ROC AUC на валидацинном наборе
best_roc_valid_data = solvers_pd[solvers_pd['roc_valid']==solvers_pd['roc_valid'].max()]

# выведем лучший результат на валидационном наборе
print('result:')
print('best solver on valid:',best_roc_valid_data.iloc[0]['solver'])
print('ROC AUC on train:', best_roc_valid_data.iloc[0]['roc_train'])
print('ROC AUC on valid:', best_roc_valid_data.iloc[0]['roc_valid'])
print('Time fit for best solver:', best_roc_valid_data.iloc[0]['time_fit'],' seconds')

# выведем полученный dataframe
solvers_pd

# time: 11m 35s

result:
best solver on valid: lbfgs
ROC AUC on train: 0.613
ROC AUC on valid: 0.617
Time fit for best solver: 0  seconds


solver  time_fit  roc_train  roc_valid  recall_0  precision_0  \
0            lbfgs         0      0.613      0.617      0.69        0.974   
1        liblinear         1      0.613      0.617      0.69        0.974   
2        newton-cg         0      0.613      0.617      0.69        0.974   
3  newton-cholesky         0      0.613      0.617      0.69        0.974   
4              sag        79      0.613      0.617      0.69        0.974   
5             saga       110      0.613      0.617      0.69        0.974   

   recall_1  precision_1  
0     0.493        0.055  
1     0.493        0.055  
2     0.492        0.055  
3     0.493        0.055  
4     0.493        0.055  
5     0.493        0.055

##### <span style="color:MediumSlateBlue">Подбор гиперпараметров модели</span>

In [1481]:
# для выбора sceler преобразвания на понадобится словарь
dict_scalers ={
    'MinMaxScaler':MinMaxScaler(),
    'RobustScaler':RobustScaler(),
    'StandardScaler':StandardScaler(),
}
# определим пространство признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'late'
count_features = dict_spaces[feature_space]

# настроим оптимизацию гипер параметров
def optuna_lg(trial):
  # задаем пространства поиска гиперпараметров
  C = trial.suggest_float('C',0.01,1)
  solver = trial.suggest_categorical('solver', ['lbfgs', 'liblinear', 'newton-cg', 'newton-cholesky'])
  class_0_weight = trial.suggest_float('class_0_weight',0.01,1)
  class_1_weight = trial.suggest_float('class_1_weight',0.01,1)
  n_last = trial.suggest_int('n_last', 10, 25,step = 1)
  class_1_percent = trial.suggest_float('class_1_percent',0.01,1)
  scaler = trial.suggest_categorical('scaler', ['MinMaxScaler', 'RobustScaler','StandardScaler'])
  random_state = trial.suggest_int('random_state', 1, 1000000)

  # создаем модель
  optuna_log_reg = linear_model.LogisticRegression(
      solver=solver,
      C=C,
      class_weight={0:class_0_weight,1:class_1_weight},
      random_state=random_state,
      max_iter=10000)

  # с помощью функции features_from_transform_data_torow извлечем  
  # из данных transform_data_torow
  # признаки сооствествующие n_last последним клиенским операциям
  list_n_last_features = features_from_transform_data_torow(n_last,count_features,25)

  # обьявим scaler
  scaler = dict_scalers[scaler]

  # загружаем обучующие наборы
  X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
  y_train_pd = pd.read_csv('target/target_train.csv')

  # поготовим данные y_train_pd к работе с функцией class_1_percent_samples
  y_train_pd.set_index('id',drop=False,inplace=True)

  # подготовим данные для обучения модели
  # с помощью функции class_1_percent_samples зададим долю 
  # класса 1
  list_c1_percent_id = class_1_percent_samples(y_train_pd,class_1_percent,random_state=random_state)[:1000000]

  # сформируем данные для обучения базовой модели
  X_train_s_balanced = scaler.fit_transform(np.array(X_train_pd.loc[list_c1_percent_id])[:,list_n_last_features])
  y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

  # освободим память от "тяжелых" и ненужных файлов
  del X_train_pd, y_train_pd
  gc.collect()

  # я не воспользовался параметром timeout метода optimize потому, что  
  # optimize отставливает поиск параметров, если время обучения 
  # превышает timeout. Мне нужно чтобы поиск параметров продолжился.
  try:
    # для модуля func_time_out упакуем обучение модели в функцию try_func
    def try_func():
            return optuna_log_reg.fit(X_train_s_balanced, y_train_balanced)
    # обучаем модель с ограничением по времени 10 минут (600 секунд)
    optuna_log_reg = func_timeout.func_timeout(600, try_func)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train_s_balanced,y_train_balanced
    gc.collect()

    # подгружаем данные для тестирования
    X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()[:,list_n_last_features]
    y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
    X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()[:,list_n_last_features]
    y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

    # сформируем данные для проверки модели
    X_train_s = scaler.transform(X_train)
    X_valid_s = scaler.transform(X_valid)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train, X_valid
    gc.collect()

    # делаем предсказание на обучающем и валидационном наборе и считаем метрики
    roc_train = metrics.roc_auc_score(y_train, optuna_log_reg.predict_proba(X_train_s)[:,1])
    roc_valid = metrics.roc_auc_score(y_valid, optuna_log_reg.predict_proba(X_valid_s)[:,1])
    f1_score = metrics.f1_score(y_valid, optuna_log_reg.predict(X_valid_s))
    recall_1 = metrics.recall_score(y_valid, optuna_log_reg.predict(X_valid_s),average=None,zero_division=0)[1]
    precision_1 = metrics.precision_score(y_valid, optuna_log_reg.predict(X_valid_s),average=None,zero_division=0)[1]

    del X_train_s, X_valid_s, y_train, y_valid
    gc.collect()

  except func_timeout.FunctionTimedOut:
    # освободим память от "тяжелых" и ненужных файлов
    del X_train_s_balanced, y_train_balanced
    gc.collect()

    # обьявим метрики пустыми значениями
    roc_train = 0
    roc_valid = 0
    f1_score = 0
    recall_1 = 0
    precision_1 = 0
    pass

  return roc_train, roc_valid, f1_score, recall_1, precision_1

In [1482]:
# cоздаем объект исследования
# чтобы модель не переобучалась минимизируем roc_train 
# и максимизируем roc_valid
optuna_study_lg = optuna.create_study(study_name='LogisticRegression_'+feature_space+'_torow', 
                               directions=['maximize','maximize','maximize','maximize','maximize'], 
                               sampler=optuna.samplers.TPESampler(),
                               pruner='Hyperband',
                               storage='sqlite:///optuna_studies.db',
                               load_if_exists=True)
# на случай удаления 
# optuna.delete_study(study_name='LogisticRegression_'+feature_space+'_torow', storage='sqlite:///optuna_studies.db')

[I 2025-04-19 12:02:38,489] Using an existing study with name 'LogisticRegression_late_torow' instead of creating a new one.


In [127]:
# ищем лучшую комбинацию гиперпараметров n_trials раз
optuna_study_lg.optimize(optuna_lg, n_trials=300)

[I 2025-04-17 10:22:09,586] Trial 0 finished with values: [0.6159276925173551, 0.6197740973156387, 0.07053151598119159, 0.9468637634838194, 0.03663003663003663] and parameters: {'C': 0.5757155410573358, 'solver': 'liblinear', 'class_0_weight': 0.4659259379041005, 'class_1_weight': 0.14183055506036926, 'n_last': 23, 'class_1_percent': 0.8507593868390638, 'scaler': 'RobustScaler', 'random_state': 58988}.
[I 2025-04-17 10:22:34,260] Trial 1 finished with values: [0.6220512295334031, 0.6251216070207947, 0.07649039774278693, 0.8393927287255294, 0.04007094903875496] and parameters: {'C': 0.29952381474892475, 'solver': 'lbfgs', 'class_0_weight': 0.04263776345629004, 'class_1_weight': 0.5975428532511, 'n_last': 19, 'class_1_percent': 0.09200041594254617, 'scaler': 'RobustScaler', 'random_state': 406814}.
[I 2025-04-17 10:22:47,098] Trial 2 finished with values: [0.6207394646013222, 0.6244728735222883, 0.0, 0.0, 0.0] and parameters: {'C': 0.09525206254043708, 'solver': 'newton-cholesky', 'class

In [1483]:
# из полученного результат соврмируем Data Frame
optuna_study_lg_pd = optuna_study_lg.trials_dataframe().dropna()
# переименуем столбы
optuna_study_lg_pd.rename(columns={
    'values_0': 'roc_train',
    'values_1': 'roc_valid',
    'values_2': 'f1_score',
    'values_3': 'recall_1',
    'values_4': 'precision_1'
},inplace=True)
# Выделим время потраченное на обучение модели
optuna_study_lg_pd.head(5)

number  roc_train  roc_valid  f1_score  recall_1  precision_1  \
0       0   0.615928   0.619774  0.070532  0.946864     0.036630   
1       1   0.622051   0.625122  0.076490  0.839393     0.040071   
2       2   0.620739   0.624473  0.000000  0.000000     0.000000   
3       3   0.591369   0.591508  0.067875  1.000000     0.035130   
4       4   0.619268   0.623129  0.067875  1.000000     0.035130   

              datetime_start          datetime_complete  \
0 2025-04-17 10:22:04.978275 2025-04-17 10:22:09.584048   
1 2025-04-17 10:22:09.590368 2025-04-17 10:22:34.257435   
2 2025-04-17 10:22:34.263664 2025-04-17 10:22:47.096764   
3 2025-04-17 10:22:47.102104 2025-04-17 10:22:50.000585   
4 2025-04-17 10:22:50.005916 2025-04-17 10:22:52.868926   

                duration  params_C  params_class_0_weight  \
0 0 days 00:00:04.605773  0.575716               0.465926   
1 0 days 00:00:24.667067  0.299524               0.042638   
2 0 days 00:00:12.833100  0.095252               0.625364   
3 0 days 00:00:02.898481  0.273275               0.483159   
4 0 days 00:00:02.863010  0.417492               0.060921   

   params_class_1_percent  params_class_1_weight  params_n_last  \
0                0.850759               0.141831             23   
1                0.092000               0.597543             19   
2                0.035238               0.226987             21   
3                0.964953               0.901376             19   
4                0.656156               0.253407             17   

   params_random_state   params_scaler    params_solver     state  
0                58988    RobustScaler        liblinear  COMPLETE  
1               406814    RobustScaler            lbfgs  COMPLETE  
2                89925    MinMaxScaler  newton-cholesky  COMPLETE  
3               288734  StandardScaler            lbfgs  COMPLETE  
4               225651    RobustScaler  newton-cholesky  COMPLETE

In [1484]:
# покаждем статистику обучения
print('Максимальное значение метрики ROC AUC на валидационном наборе:',round(optuna_study_lg_pd['roc_valid'].max(),3))
print('Среднее значение метрики ROC AUC на валидационном наборе:',round(optuna_study_lg_pd['roc_valid'].mean(),3))
print('Максимальное значение метрики f1_score на валидационном наборе:',round(optuna_study_lg_pd['f1_score'].max(),3))
print('Среднее значение метрики f1_score на валидационном наборе:',round(optuna_study_lg_pd['f1_score'].mean(),3))
print('Максимальное значение метрики recall_1 на валидационном наборе:',round(optuna_study_lg_pd['recall_1'].max(),3))
print('Среднее значение метрики recall_1 на валидационном наборе:',round(optuna_study_lg_pd['recall_1'].mean(),3))
print('Максимальное значение метрики precision_1 на валидационном наборе:',round(optuna_study_lg_pd['precision_1'].max(),3))
print('Среднее значение метрики precision_1 на валидационном наборе:',round(optuna_study_lg_pd['precision_1'].mean(),3))

Максимальное значение метрики ROC AUC на валидационном наборе: 0.626
Среднее значение метрики ROC AUC на валидационном наборе: 0.622
Максимальное значение метрики f1_score на валидационном наборе: 0.114
Среднее значение метрики f1_score на валидационном наборе: 0.078
Максимальное значение метрики recall_1 на валидационном наборе: 1.0
Среднее значение метрики recall_1 на валидационном наборе: 0.402
Максимальное значение метрики precision_1 на валидационном наборе: 0.25
Среднее значение метрики precision_1 на валидационном наборе: 0.078


In [1488]:
# Визуализируем метрики полученные при optuna оптимизации
fig = px.scatter(
    data_frame=optuna_study_lg_pd[
                                (optuna_study_lg_pd['roc_valid']>0.9*optuna_study_lg_pd['roc_valid'].max())&
                                (optuna_study_lg_pd['f1_score']>0.99*optuna_study_lg_pd['f1_score'].max())],
    x='number', #ось абсцисс
    y=['roc_train','roc_valid','recall_1','precision_1','f1_score'], #ось ординат
)
fig.update_layout(
    title ={
        'text':'Зависимость качества модели от trials optuna', # Имя рабочей плоскости
        'font':{'size':35,'family':"Times New Roman"}, # размер и стиль написания имени рабочей плоскости
        'x':0.5, # Смешение имени по оси "x" на половину рабочей плоскости
        },
    height =800,# Высота рабочей плоскости
    width = 1350, # Ширина рабочей плоскости
    bargap=0.2, # Добавил расстояния между столбами гистограммы
    xaxis_title='trials optuna',
    yaxis_title='Величина метрики')
fig.update_xaxes(showspikes=True)
fig.update_yaxes(showspikes=True)

fig.show()

<span style="color:Blue">

Вывод:  

Их всех выбираем точку $number =289$.   
В этой точке одно из самых больших значений $ROC AUC$.  
Посмотрим каким значениям гиперпараметров соотвествует выбранная точка.

In [1489]:
# определим номер лучшге варианта
best_optuna_number = 289

# сформируем словарь лучших гипирпарметров RandomForestClassifier
best_param_lr_torow = {
    'C' : round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_C'].iloc[0],3),
    'class_weight' : {0:round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_class_0_weight'].iloc[0],3),
                      1:round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_class_1_weight'].iloc[0],3)},
    }
# создадим перменные
best_n_last = int(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_n_last'].iloc[0])
best_scaler = optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_scaler'].iloc[0]
best_class_1_percent = optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_class_1_percent'].iloc[0]
best_random_state = int(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_random_state'].iloc[0])
# Выведем принятые наилучшие праметры
print('best C:',best_param_lr_torow['C'])
print('best class 0 weight:',best_param_lr_torow['class_weight'][0])
print('best class 1 weight:',best_param_lr_torow['class_weight'][1])

print('best class 1 percent:',round(best_class_1_percent,3))
print('best scaler:',best_scaler)
print('best n_last:',round(best_n_last,3))
print('best best random state:',best_random_state)
print('time for best train:',round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['duration'].iloc[0].seconds/60),'minutes')

print()
print('ROC AUC на обучающем наборе:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['roc_train'].iloc[0],3))
print('ROC AUC на валидационном наборе:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['roc_valid'].iloc[0],3))
print('precision класса 1:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['precision_1'].iloc[0],3))
print('recall класса 1:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['recall_1'].iloc[0],3))

best C: 0.046
best class 0 weight: 0.241
best class 1 weight: 0.729
best class 1 percent: 0.178
best scaler: MinMaxScaler
best n_last: 19
best best random state: 87365
time for best train: 0 minutes

ROC AUC на обучающем наборе: 0.62
ROC AUC на валидационном наборе: 0.624
precision класса 1: 0.079
recall класса 1: 0.199


##### <span style="color:MediumSlateBlue">Обучение модели с лучшими параметрами</span>

In [1490]:
# для выбора sceler преобразвания на понадобится словарь
dict_scalers ={
    'MinMaxScaler':MinMaxScaler(),
    'RobustScaler':RobustScaler(),
    'StandardScaler':StandardScaler(),
}

# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'late'
count_features = dict_spaces[feature_space]

# с помощью функции features_from_transform_data_torow извлечем  
# из данных transform_data_torow_25
# признаки сооствествующие n_last последним клиенским операциям
list_n_last_features = features_from_transform_data_torow(best_n_last,count_features,25)

# обьявим scaler
scaler = dict_scalers[best_scaler]

# загружаем обучующие наборы
X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)

# подготовим данные для обучения модели
# с помощью функции class_1_percent_samples зададим долю 
# класса 1
list_c1_percent_id = class_1_percent_samples(y_train_pd,best_class_1_percent,random_state=best_random_state)[:1000000]

# сформируем данные для обучения базовой модели
X_train_s_balanced = scaler.fit_transform(np.array(X_train_pd.loc[list_c1_percent_id])[:,list_n_last_features])
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

# освободим память от "тяжелых" и ненужных файлов
del X_train_pd, y_train_pd
gc.collect()


# обучаем модель LogisticRegression с наилучшеми параметрами
logistic_regression = linear_model.LogisticRegression(
        **best_param_lr_torow,
        random_state=best_random_state,
        max_iter=10000)
logistic_regression.fit(X_train_s_balanced,y_train_balanced)

# удаляем крупные файлы чтобы высвободить память 
del X_train_s_balanced,y_train_balanced
gc.collect()

# подгружаем данные для тестирования
X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()[:,list_n_last_features]
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()[:,list_n_last_features]
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()
    
# сформируем данные для проверки модели
X_train_s = scaler.transform(X_train)
X_valid_s = scaler.transform(X_valid)

# удаляем крупные файлы чтобы высвободить память 
del X_train, X_valid
gc.collect()

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_lr_pred_proba = logistic_regression.predict_proba(X_train_s)[:,1]
y_valid_lr_pred_proba = logistic_regression.predict_proba(X_valid_s)[:,1]

# Делаем предсказание для валидационной выборки
y_valid_lr_pred = logistic_regression.predict(X_valid_s)

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_lr_pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_lr_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_lr_pred,zero_division=0))

# time: 2m 40s

ROC AUC на обучающем наборе 0.62
ROC AUC на валидационном наборе 0.624
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.97      0.92      0.94     68747
           1       0.08      0.20      0.11      2503

    accuracy                           0.89     71250
   macro avg       0.52      0.56      0.53     71250
weighted avg       0.94      0.89      0.91     71250



#### <span style="color:MediumBlue">Построение модели Random Forest Classifier</span>

##### <span style="color:MediumSlateBlue">Формирование данных для обучения</span>

Анализ исходных данных, в частности target, показал что представленные данные   
имееют перекос: 96% клиентов у которых не случился дефолт (flag = 0),    
против 4 % - для которых произошел дефолт (flag = 1).  
С помощью функции class_1_percent_samples, сформируем сбаланисрованную выборку  
для обучения моделей.
За основу сбалансировных данных возьмем данные клиентов с дефолтом  
и к ним будем добирать необходимое количество клиентов до сбалансированности. 


Функция class_1_percent_samples принемает две переменные:
- target_data - массив с id и целевой переменной
- class_1_percent - процент класса 1 в результирующем массиве

In [1304]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'late'
count_features = dict_spaces[feature_space]

In [1305]:
# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

In [1306]:
# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)
y_train_pd.head(4)

id  flag
id                    
1825800  1825800     0
2166483  2166483     0
2534345  2534345     0
1803283  1803283     0

In [1307]:
# взглянем на сблансиорованность данных в y_train
y_train_pd['flag'].value_counts(normalize=True)

flag
0    0.964242
1    0.035758
Name: proportion, dtype: float64

In [1308]:
# сбалансируем данные в y_train_pd
list_c1_percent_id = class_1_percent_samples(y_train_pd,0.5)
# list_c1_percent_features - список 'id' из y_train_pd соотвествующих  
# заданному проценту класса 1
len(list_c1_percent_id)

45860

In [1309]:
# проверим сбалансированность полученного y_train
y_train_pd.loc[list_c1_percent_id]['flag'].value_counts(normalize=True)

flag
1    0.5
0    0.5
Name: proportion, dtype: float64

*transform_data_torow*, показываеются последние N операций клиента.  
В данных в *date_torow*, собраны последние 25 операций клиентов.

Предварительный анализ показывает, что медиальное значение количества клиентских  
операций равно 7. Поэтому, для начала, будем показывать моделе $n_{last} = 7$   
последних клиентских операций.

Для извлечения из *transform_data_torow_25* необходимого количества последних клиенских  
операций ($n_{last}$) используем функцию features_from_transform_data_torow.

Функция features_from_transform_data_torow примает следующие аргументы:
- $n_{last} = 7$ - необходимое количество последних клиентских операций; 
- $n_{groups} = 8$ - количество признаков в $date$ $features$;
- $N_{last} = 25$ - количество $n_{last}$ операций, показанных в transform_data_torow_25


In [1310]:
# с помощью функции features_from_transform_data_torow извлечем  
# из данных transform_data_torow_25
# признаки сооствествующие 7 последним клиенским операциям
list_n_last_features = features_from_transform_data_torow(7,count_features,25)

In [1311]:
# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']
# сформируем данные для проверики модели
X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

In [1312]:
# посмотрим на структуру данных в X_train_balanced
X_train_balanced.head(2)

f1  f2  f3  f4  f5  f6  f7  f8  f9  f10  ...  f291  f292  f293  f294  \
id                                                ...                           
2335465   6   6   6   6   6   6   6   6   6    6  ...     2     2     0     0   
390270    6   6   6   6   6   6   0   0   0    0  ...     0     0     0     0   

         f295  f296  f297  f298  f299  f300  
id                                           
2335465     0     0     0     0     0     0  
390270      0     0     0     0     0     0  

[2 rows x 300 columns]

In [1313]:
# посмотрим на структуру данных в y_train_balanced
y_train_balanced.head(2)

id
2335465    1
390270     1
Name: flag, dtype: int64

In [1314]:
# проверим что выборки действительно совпадают по id
X_train_balanced.index.to_list() == y_train_balanced.index.to_list()

True

##### <span style="color:MediumSlateBlue">Baseline обучение модели RandomForestClassifier</span>

In [1315]:
# обучаем модель логистической регрессии
# чтобы модель пыталась найти связь во всех признаках
random_forest = RandomForestClassifier(random_state=42, n_jobs=-1)
random_forest.fit(np.array(X_train_balanced)[:,list_n_last_features],np.array(y_train_balanced))

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_rf__pred_proba = random_forest.predict_proba(X_train[:,list_n_last_features])[:,1]
y_valid_rf_pred_proba = random_forest.predict_proba(X_valid[:,list_n_last_features])[:,1]

# Делаем предсказание для валидационной выборки
y_valid_rf_pred = random_forest.predict(X_valid[:,list_n_last_features])

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_rf__pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_rf_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_rf_pred))

# time: 2m 5s

ROC AUC на обучающем наборе 0.694
ROC AUC на валидационном наборе 0.587
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.97      0.68      0.80     68747
           1       0.05      0.48      0.09      2503

    accuracy                           0.67     71250
   macro avg       0.51      0.58      0.45     71250
weighted avg       0.94      0.67      0.78     71250



##### <span style="color:MediumSlateBlue">Подбор гиперпараметров модели</span>

In [1491]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'late'
count_features = dict_spaces[feature_space]

# настроим оптимизацию гипер параметров
def optuna_rf(trial):
  # задаем пространства поиска гиперпараметров
  # задаем пространства поиска гиперпараметров
  n_estimators = trial.suggest_int('n_estimators', 50, 150,step = 5)
  criterion = trial.suggest_categorical('criterion',['gini', 'entropy', 'log_loss'])
  max_depth = trial.suggest_int('max_depth', 9, 20,step = 1)
  min_samples_split = trial.suggest_int('min_samples_split', 5, 15,step = 1)
  min_samples_leaf = trial.suggest_int('min_samples_leaf', 5, 25,step = 1)
  max_features = trial.suggest_float('max_features',0.1,1)
  max_samples = trial.suggest_float('max_samples',0.1,1)
  class_0_weight = trial.suggest_float('class_0_weight',0.01,1)
  class_1_weight = trial.suggest_float('class_1_weight',0.01,1)
  n_last = trial.suggest_int('n_last', 5, 25,step = 1)
  class_1_percent = trial.suggest_float('class_1_percent',0.01,0.9)
  random_state = trial.suggest_int('random_state', 1, 1000000)


  # создаем модель
  optuna_random_forest = RandomForestClassifier(
      n_estimators = n_estimators, 
      criterion = criterion,
      max_depth = max_depth,
      min_samples_split = min_samples_split,  
      min_samples_leaf = min_samples_leaf,
      max_features=max_features,
      max_samples=max_samples,
      class_weight={0:class_0_weight,1:class_1_weight},
      n_jobs=-1,
      random_state=random_state)

  # с помощью функции features_from_transform_data_torow извлечем  
  # из данных transform_data_torow
  # признаки сооствествующие n_last последним клиенским операциям
  list_n_last_features = features_from_transform_data_torow(n_last,count_features,25)

  # загружаем обучующие наборы
  X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
  y_train_pd = pd.read_csv('target/target_train.csv')

  # поготовим данные y_train_pd к работе с функцией class_1_percent_samples
  y_train_pd.set_index('id',drop=False,inplace=True)

  # подготовим данные для обучения модели
  # с помощью функции class_1_percent_samples зададим долю 
  # класса 1
  list_c1_percent_id = class_1_percent_samples(y_train_pd,class_1_percent,random_state=random_state)[:1000000]

  # сформируем данные для обучения базовой модели
  X_train_balanced = np.array(X_train_pd.loc[list_c1_percent_id])[:,list_n_last_features]
  y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

  # освободим память от "тяжелых" и ненужных файлов
  del X_train_pd, y_train_pd
  gc.collect()

  # я не воспользовался параметром timeout метода optimize потому, что  
  # optimize отставливает поиск параметров, если время обучения 
  # превышает timeout. Мне нужно чтобы поиск параметров продолжился.
  try:
    # для модуля func_time_out упакуем обучение модели в функцию try_func
    def try_func():
            return optuna_random_forest.fit(X_train_balanced,y_train_balanced)
    # обучаем модель с ограничением по времени 10 минут (600 секунд)
    optuna_random_forest = func_timeout.func_timeout(600, try_func)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train_balanced, y_train_balanced
    gc.collect()

    # подгружаем данные для тестирования
    X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()[:,list_n_last_features]
    y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
    X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()[:,list_n_last_features]
    y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

    # делаем предсказание на обучающем и валидационном наборе и считаем метрики
    roc_train = metrics.roc_auc_score(y_train, optuna_random_forest.predict_proba(X_train)[:,1])
    roc_valid = metrics.roc_auc_score(y_valid, optuna_random_forest.predict_proba(X_valid)[:,1])
    f1_score = metrics.f1_score(y_valid, optuna_random_forest.predict(X_valid))
    recall_1 = metrics.recall_score(y_valid, optuna_random_forest.predict(X_valid),average=None,zero_division=0)[1]
    precision_1 = metrics.precision_score(y_valid, optuna_random_forest.predict(X_valid),average=None,zero_division=0)[1]

    # удаляем крупные файлы чтобы высвободить память 
    del X_train, X_valid, y_train, y_valid 
    gc.collect()

  except func_timeout.FunctionTimedOut:
    # освободим память от "тяжелых" и ненужных файлов
    del X_train_balanced, y_train_balanced
    gc.collect()

    # обьявим метрики пустыми значениями
    roc_train = 0
    roc_valid = 0
    f1_score = 0
    recall_1 = 0
    precision_1 = 0
    pass

  return roc_train, roc_valid, f1_score, recall_1, precision_1

In [1492]:
# так как Random Forest склонен к переобучению 
# попробуем направить optimize в сторону уменьшения roc_train
# cоздаем объект исследования
optuna_study_rf = optuna.create_study(study_name='RandomForestClassifier_'+feature_space+'_torow', 
                               directions=['minimize','maximize','maximize','maximize','maximize'], 
                               sampler=optuna.samplers.TPESampler(),
                               pruner='Hyperband',
                               storage='sqlite:///optuna_studies.db',
                               load_if_exists=True)
# на случай удаления 
# optuna.delete_study(study_name='RandomForestClassifier_'+feature_space+'_torow', storage='sqlite:///optuna_studies.db')

[I 2025-04-19 12:05:04,327] Using an existing study with name 'RandomForestClassifier_late_torow' instead of creating a new one.


In [158]:
# ищем лучшую комбинацию гиперпараметров n_trials раз
optuna_study_rf.optimize(optuna_rf, n_trials=300)

[I 2025-04-17 11:17:15,459] Trial 0 finished with values: [0.6407795351254109, 0.6228875531915123, 0.03597883597883598, 0.02037554934079105, 0.1536144578313253] and parameters: {'n_estimators': 60, 'criterion': 'entropy', 'max_depth': 20, 'min_samples_split': 9, 'min_samples_leaf': 17, 'max_features': 0.3884473011436766, 'max_samples': 0.25906702743001847, 'class_0_weight': 0.423692329319405, 'class_1_weight': 0.24475502407982638, 'n_last': 23, 'class_1_percent': 0.3013539340950018, 'random_state': 679654}.
[I 2025-04-17 11:17:20,102] Trial 1 finished with values: [0.6301502253732905, 0.6202915731343344, 0.02929329915781765, 0.015980823012385136, 0.17543859649122806] and parameters: {'n_estimators': 95, 'criterion': 'log_loss', 'max_depth': 11, 'min_samples_split': 12, 'min_samples_leaf': 5, 'max_features': 0.5140886382695055, 'max_samples': 0.2020988413983485, 'class_0_weight': 0.35586742803696064, 'class_1_weight': 0.1358986463621899, 'n_last': 18, 'class_1_percent': 0.29765230181639

In [1493]:
# из полученного результат соврмируем Data Frame
optuna_study_rf_pd = optuna_study_rf.trials_dataframe().dropna()
# переименуем столбы
optuna_study_rf_pd.rename(columns={
    'values_0': 'roc_train',
    'values_1': 'roc_valid',
    'values_2': 'f1_score',
    'values_3': 'recall_1',
    'values_4': 'precision_1'
},inplace=True)
optuna_study_rf_pd.sort_values(by='precision_1').drop(['datetime_start','datetime_complete','duration'],axis=1)

number  roc_train  roc_valid  f1_score  recall_1  precision_1  \
51       51   0.626299   0.619786  0.000000  0.000000     0.000000   
208     208   0.612200   0.613808  0.000000  0.000000     0.000000   
108     108   0.639522   0.621718  0.000000  0.000000     0.000000   
29       29   0.617437   0.617335  0.000000  0.000000     0.000000   
154     154   0.640893   0.620187  0.000000  0.000000     0.000000   
..      ...        ...        ...       ...       ...          ...   
68       68   0.629252   0.621911  0.010886  0.005593     0.202899   
86       86   0.653534   0.620868  0.019764  0.010388     0.203125   
140     140   0.626204   0.622952  0.007075  0.003596     0.219512   
90       90   0.640246   0.620465  0.003180  0.001598     0.307692   
190     190   0.611782   0.614171  0.002389  0.001199     0.333333   

     params_class_0_weight  params_class_1_percent  params_class_1_weight  \
51                0.781329                0.172151               0.625395   
208               0.494885                0.286404               0.072756   
108               0.864214                0.219777               0.010969   
29                0.908200                0.445164               0.129376   
154               0.475419                0.042579               0.172354   
..                     ...                     ...                    ...   
68                0.715035                0.205275               0.584654   
86                0.179384                0.085897               0.421157   
140               0.848131                0.308692               0.467423   
90                0.636362                0.340324               0.112559   
190               0.721771                0.205903               0.514846   

    params_criterion  params_max_depth  params_max_features  \
51          log_loss                11             0.225929   
208             gini                15             0.126457   
108             gini                15             0.112532   
29          log_loss                12             0.600816   
154             gini                13             0.414848   
..               ...               ...                  ...   
68           entropy                12             0.313657   
86           entropy                15             0.559553   
140             gini                14             0.100981   
90              gini                15             0.123485   
190             gini                 9             0.194931   

     params_max_samples  params_min_samples_leaf  params_min_samples_split  \
51             0.184947                       24                         5   
208            0.171915                       21                         9   
108            0.715803                       11                         8   
29             0.122702                       19                        11   
154            0.151525                        9                        10   
..                  ...                      ...                       ...   
68             0.175353                       20                         6   
86             0.330814                       20                         6   
140            0.205894                       22                        15   
90             0.942112                        7                         9   
190            0.225731                       20                         5   

     params_n_estimators  params_n_last  params_random_state     state  
51                   105             14               649164  COMPLETE  
208                  145              5                23209  COMPLETE  
108                  130             17               572802  COMPLETE  
29                    65              9               995301  COMPLETE  
154                  130             18               462765  COMPLETE  
..                   ...            ...                  ...       ...  
68                   105          

In [1494]:
# покаждем статистику обучения
print('Максимальное значение метрики ROC AUC на валидационном наборе:',round(optuna_study_rf_pd['roc_valid'].max(),3))
print('Среднее значение метрики ROC AUC на валидационном наборе:',round(optuna_study_rf_pd['roc_valid'].mean(),3))
print('Максимальное значение метрики f1_score на валидационном наборе:',round(optuna_study_rf_pd['f1_score'].max(),3))
print('Среднее значение метрики f1_score на валидационном наборе:',round(optuna_study_rf_pd['f1_score'].mean(),3))
print('Максимальное значение метрики recall_1 на валидационном наборе:',round(optuna_study_rf_pd['recall_1'].max(),3))
print('Среднее значение метрики recall_1 на валидационном наборе:',round(optuna_study_rf_pd['recall_1'].mean(),3))
print('Максимальное значение метрики precision_1 на валидационном наборе:',round(optuna_study_rf_pd['precision_1'].max(),3))
print('Среднее значение метрики precision_1 на валидационном наборе:',round(optuna_study_rf_pd['precision_1'].mean(),3))

Максимальное значение метрики ROC AUC на валидационном наборе: 0.625
Среднее значение метрики ROC AUC на валидационном наборе: 0.618
Максимальное значение метрики f1_score на валидационном наборе: 0.113
Среднее значение метрики f1_score на валидационном наборе: 0.077
Максимальное значение метрики recall_1 на валидационном наборе: 1.0
Среднее значение метрики recall_1 на валидационном наборе: 0.442
Максимальное значение метрики precision_1 на валидационном наборе: 0.333
Среднее значение метрики precision_1 на валидационном наборе: 0.068


In [1510]:
# Построим зависимость метрик качества модели от number

fig = px.scatter(
    data_frame=optuna_study_rf_pd[(optuna_study_rf_pd['roc_valid']>=0.99*optuna_study_rf_pd['roc_valid'].max())&
                                  (optuna_study_rf_pd['f1_score']>=0.99*optuna_study_rf_pd['f1_score'].max())],
    x='number', #ось абсцисс
    y=['roc_valid','roc_train','precision_1','recall_1','f1_score'], #ось ординат
)
fig.update_layout(
    title ={
        'text':'Зависимость метрик качества модели от number', # Имя рабочей плоскости
        'font':{'size':35,'family':"Times New Roman"}, # размер и стиль написания имени рабочей плоскости
        'x':0.5, # Смешение имени по оси "x" на половину рабочей плоскости
        },
    height =800,# Высота рабочей плоскости
    width = 1350, # Ширина рабочей плоскости
    bargap=0.2, # Добавил расстояния между столбами гистограммы
    xaxis_title='Величина метрики ROC Valid',
    yaxis_title='Величина параметра')
fig.update_xaxes(showspikes=True)
fig.update_yaxes(showspikes=True)

fig.show()

<span style="color:Blue">

Вывод:  

Их всех выбираем точку $number =96$.   
В этой точке оптимальные значения метрик $recall_1$ и $precision_1$, а  
также относительно высокая метрика $ROC AUC$.   
Посмотрим каким значениям гиперпараметров соотвествует выбраннаяточка.

In [1511]:
# определим номер лучшге варианта
best_optuna_number = 96

# сформируем словарь лучших гипирпарметров RandomForestClassifier
best_param_rf = {
    'n_estimators' : int(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_n_estimators'].iloc[0]),
    'criterion': optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_criterion'].iloc[0],
    'max_depth' : optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_max_depth'].iloc[0],
    'min_samples_split': optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_min_samples_split'].iloc[0],
    'min_samples_leaf' : optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_min_samples_leaf'].iloc[0],
    'max_features': optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_max_features'].iloc[0],
    'max_samples' : optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_max_samples'].iloc[0],
    'class_weight' : {0:optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_class_0_weight'].iloc[0],
                      1:optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_class_1_weight'].iloc[0]}
    }
# определим перменные для лучших значений параметров
best_n_last = optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_n_last'].iloc[0]
best_class_1_percent = optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_class_1_percent'].iloc[0]
best_random_state = optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_random_state'].iloc[0]


# Выведем принятые наилучшие праметры
print('best n estimators:',best_param_rf['n_estimators'])
print('best criterion:',best_param_rf['criterion'])
print('best max depth:',best_param_rf['max_depth'])
print('best min samples split:',best_param_rf['min_samples_split'])
print('best min samples leaf:',best_param_rf['min_samples_leaf'])
print('best max features(%):',round(best_param_rf['max_features'],3))
print('best max samples(%):',round(best_param_rf['max_samples'],3))
print('best class 0 weight:',round(best_param_rf['class_weight'][0],3))
print('best class 1 weight:',round(best_param_rf['class_weight'][1],3))

print('best class 1 percent:',round(best_class_1_percent,3))
print('best n last:',best_n_last)
print('best random state:',best_random_state)
print('time for best train:',round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['duration'].iloc[0].seconds/60),'minutes')

print()
print('ROC AUC на обучающем наборе:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['roc_train'].iloc[0],3))
print('ROC AUC на валидационном наборе:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['roc_valid'].iloc[0],3))
print('precision класса 1:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['precision_1'].iloc[0],3))
print('recall класса 1:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['recall_1'].iloc[0],3))

best n estimators: 140
best criterion: gini
best max depth: 16
best min samples split: 8
best min samples leaf: 20
best max features(%): 0.127
best max samples(%): 0.68
best class 0 weight: 0.474
best class 1 weight: 0.938
best class 1 percent: 0.266
best n last: 18
best random state: 467112
time for best train: 0 minutes

ROC AUC на обучающем наборе: 0.64
ROC AUC на валидационном наборе: 0.625
precision класса 1: 0.075
recall класса 1: 0.221


##### <span style="color:MediumSlateBlue">Обучение модели с лучшими параметрами</span>

In [1512]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'late'
count_features = dict_spaces[feature_space]

# с помощью функции features_from_transform_data_torow извлечем  
# из данных transform_data_torow
# признаки сооствествующие n_last последним клиенским операциям
list_n_last_features = features_from_transform_data_torow(best_n_last,count_features,25)

# загружаем обучующие наборы
X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)

# подготовим данные для обучения модели
# с помощью функции class_1_percent_samples зададим долю 
# класса 1
list_c1_percent_id = class_1_percent_samples(y_train_pd,best_class_1_percent,random_state=best_random_state)[:1000000]

# сформируем данные для обучения базовой модели
X_train_balanced = np.array(X_train_pd.loc[list_c1_percent_id])[:,list_n_last_features]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

# освободим память от "тяжелых" и ненужных файлов
del X_train_pd, y_train_pd
gc.collect()

# обучаем модель RandomForestClassifier с наилучшеми параметрами
random_forest = RandomForestClassifier(
        **best_param_rf,
        n_jobs=-1,
        random_state=best_random_state)
random_forest.fit(X_train_balanced, y_train_balanced)

# освободим память от "тяжелых" и ненужных файлов
del X_train_balanced, y_train_balanced
gc.collect()


# подгружаем данные для тестирования
X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()[:,list_n_last_features]
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()[:,list_n_last_features]
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_rf__pred_proba = random_forest.predict_proba(X_train)[:,1]
y_valid_rf_pred_proba = random_forest.predict_proba(X_valid)[:,1]

# Делаем предсказание для валидационной выборки
y_valid_rf_pred = random_forest.predict(X_valid)

# удаляем крупные файлы чтобы высвободить память 
del X_train, X_valid
gc.collect()

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_rf__pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_rf_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_rf_pred,zero_division=0))

# time: 2m 10s

ROC AUC на обучающем наборе 0.64
ROC AUC на валидационном наборе 0.625
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.97      0.90      0.93     68747
           1       0.07      0.22      0.11      2503

    accuracy                           0.88     71250
   macro avg       0.52      0.56      0.52     71250
weighted avg       0.94      0.88      0.90     71250



#### <span style="color:MediumBlue">Построение модели Gradient Boosting Classifier</span>

##### <span style="color:MediumSlateBlue">Формирование данных для обучения</span>

Анализ исходных данных, в частности target, показал что представленные данные   
имееют перекос: 96% клиентов у которых не случился дефолт (flag = 0),    
против 4 % - для которых произошел дефолт (flag = 1).  
С помощью функции class_1_percent_samples, сформируем сбаланисрованную выборку  
для обучения моделей.
За основу сбалансировных данных возьмем данные клиентов с дефолтом  
и к ним будем добирать необходимое количество клиентов до сбалансированности. 


Функция class_1_percent_samples принемает две переменные:
- target_data - массив с id и целевой переменной
- class_1_percent - процент класса 1 в результирующем массиве

In [1513]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'late'
count_features = dict_spaces[feature_space]

In [1514]:
# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

In [1515]:
# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)
y_train_pd.head(4)

id  flag
id                    
1825800  1825800     0
2166483  2166483     0
2534345  2534345     0
1803283  1803283     0

In [1516]:
# взглянем на сблансиорованность данных в y_train
y_train_pd['flag'].value_counts(normalize=True)

flag
0    0.964242
1    0.035758
Name: proportion, dtype: float64

In [1517]:
# сбалансируем данные в y_train_pd
list_c1_percent_id = class_1_percent_samples(y_train_pd,0.5)
# list_c1_percent_features - список 'id' из y_train_pd соотвествующих  
# заданному проценту класса 1
len(list_c1_percent_id)

45860

In [1518]:
# проверим сбалансированность полученного y_train
y_train_pd.loc[list_c1_percent_id]['flag'].value_counts(normalize=True)

flag
1    0.5
0    0.5
Name: proportion, dtype: float64

*transform_data_torow*, показываеются последние N операций клиента.  
В данных в *date_torow*, собраны последние 25 операций клиентов.

Предварительный анализ показывает, что медиальное значение количества клиентских  
операций равно 7. Поэтому, для начала, будем показывать моделе $n_{last} = 7$   
последних клиентских операций.

Для извлечения из *transform_data_torow_25* необходимого количества последних клиенских  
операций ($n_{last}$) используем функцию features_from_transform_data_torow.

Функция features_from_transform_data_torow примает следующие аргументы:
- $n_{last} = 7$ - необходимое количество последних клиентских операций; 
- $n_{groups} = 8$ - количество признаков в $date$ $features$;
- $N_{last} = 25$ - количество $n_{last}$ операций, показанных в transform_data_torow_25


In [1519]:
# с помощью функции features_from_transform_data_torow извлечем  
# из данных transform_data_torow_25
# признаки сооствествующие 7 последним клиенским операциям
list_n_last_features = features_from_transform_data_torow(7,count_features,25)

In [1520]:
# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']
# сформируем данные для проверики модели
X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

In [1521]:
# посмотрим на структуру данных в X_train_balanced
X_train_balanced.head(2)

f1  f2  f3  f4  f5  f6  f7  f8  f9  f10  ...  f291  f292  f293  f294  \
id                                                ...                           
2335465   6   6   6   6   6   6   6   6   6    6  ...     2     2     0     0   
390270    6   6   6   6   6   6   0   0   0    0  ...     0     0     0     0   

         f295  f296  f297  f298  f299  f300  
id                                           
2335465     0     0     0     0     0     0  
390270      0     0     0     0     0     0  

[2 rows x 300 columns]

In [1522]:
# посмотрим на структуру данных в y_train_balanced
y_train_balanced.head(2)

id
2335465    1
390270     1
Name: flag, dtype: int64

In [1523]:
# проверим что выборки действительно совпадают по id
X_train_balanced.index.to_list() == y_train_balanced.index.to_list()

True

##### <span style="color:MediumSlateBlue">Baseline обучение модели Hist Gradient Boosting Classifier</span>

In [1524]:
# обучаем модель Gradient Boosting Classifier
gradient_boosting = HistGradientBoostingClassifier(random_state=42)
gradient_boosting.fit(np.array(X_train_balanced)[:,list_n_last_features],np.array(y_train_balanced))

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_rf__pred_proba = gradient_boosting.predict_proba(X_train[:,list_n_last_features])[:,1]
y_valid_rf_pred_proba = gradient_boosting.predict_proba(X_valid[:,list_n_last_features])[:,1]

# Делаем предсказание для валидационной выборки
y_valid_rf_pred = gradient_boosting.predict(X_valid[:,list_n_last_features])

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_rf__pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_rf_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_rf_pred))

# time: 

ROC AUC на обучающем наборе 0.62
ROC AUC на валидационном наборе 0.616
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.97      0.70      0.81     68747
           1       0.05      0.48      0.10      2503

    accuracy                           0.69     71250
   macro avg       0.51      0.59      0.46     71250
weighted avg       0.94      0.69      0.79     71250



##### <span style="color:MediumSlateBlue">Подбор гиперпараметров модели</span>

In [1525]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'late'
count_features = dict_spaces[feature_space]

# настроим оптимизацию гипер параметров
def optuna_hgbc(trial):
  # задаем пространства поиска гиперпараметров
  learning_rate = trial.suggest_float('learning_rate',0.2,0.6)
  max_iter = trial.suggest_int('max_iter', 50, 300,step = 1)
  max_leaf_nodes = trial.suggest_int('max_leaf_nodes', 2, 50,step = 1)
  max_depth = trial.suggest_int('max_depth', 1, 15,step = 1)
  min_samples_leaf = trial.suggest_int('min_samples_leaf', 1, 50,step = 1)
  max_features = trial.suggest_float('max_features',0.1,1)
  l2_regularization = trial.suggest_float('l2_regularization',0.01,1)
  class_0_weight = trial.suggest_float('class_0_weight',0.01,1)
  class_1_weight = trial.suggest_float('class_1_weight',0.01,1)
  n_last = trial.suggest_int('n_last', 5, 25,step = 1)
  class_1_percent = trial.suggest_float('class_1_percent',0.01,1)
  random_state = trial.suggest_int('random_state', 1, 1000000)


  # создаем модель
  optuna_gradient_boosting = HistGradientBoostingClassifier(
      learning_rate= learning_rate,
      max_iter = max_iter,
      max_leaf_nodes =max_leaf_nodes,
      max_depth = max_depth,
      min_samples_leaf = min_samples_leaf,
      max_features=max_features,
      l2_regularization = l2_regularization,
      class_weight={0:class_0_weight,1:class_1_weight},
      random_state=42)

  # с помощью функции features_from_transform_data_torow извлечем  
  # из данных transform_data_torow
  # признаки сооствествующие n_last последним клиенским операциям
  list_n_last_features = features_from_transform_data_torow(n_last,count_features,25)

  # загружаем обучующие наборы
  X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
  y_train_pd = pd.read_csv('target/target_train.csv')

  # поготовим данные y_train_pd к работе с функцией class_1_percent_samples
  y_train_pd.set_index('id',drop=False,inplace=True)

  # подготовим данные для обучения модели
  # с помощью функции class_1_percent_samples зададим долю класса 1
  list_c1_percent_id = class_1_percent_samples(y_train_pd,class_1_percent,random_state=random_state)[:1000000]

  # сформируем данные для обучения модели
  X_train_balanced = np.array(X_train_pd.loc[list_c1_percent_id])[:,list_n_last_features]
  y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

  # освободим память от "тяжелых" и ненужных файлов
  del X_train_pd, y_train_pd
  gc.collect()

  # я не воспользовался параметром timeout метода optimize потому, что  
  # optimize отставливает поиск параметров, если время обучения 
  # превышает timeout. Мне нужно чтобы поиск параметров продолжился.
  try:
    # для модуля func_time_out упакуем обучение модели в функцию try_func
    def try_func():
            return optuna_gradient_boosting.fit(X_train_balanced,y_train_balanced)
    # обучаем модель с ограничением по времени 10 минут (600 секунд)
    optuna_gradient_boosting = func_timeout.func_timeout(600, try_func)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train_balanced, y_train_balanced
    gc.collect()

    # подгружаем данные для тестирования
    X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()[:,list_n_last_features]
    y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
    X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()[:,list_n_last_features]
    y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

    # делаем предсказание на обучающем и валидационном наборе и считаем метрики
    roc_train = metrics.roc_auc_score(y_train, optuna_gradient_boosting.predict_proba(X_train)[:,1])
    roc_valid = metrics.roc_auc_score(y_valid, optuna_gradient_boosting.predict_proba(X_valid)[:,1])
    f1_score = metrics.f1_score(y_valid, optuna_gradient_boosting.predict(X_valid))
    recall_1 = metrics.recall_score(y_valid, optuna_gradient_boosting.predict(X_valid),average=None,zero_division=0)[1]
    precision_1 = metrics.precision_score(y_valid, optuna_gradient_boosting.predict(X_valid),average=None,zero_division=0)[1]

    # удаляем крупные файлы чтобы высвободить память 
    del X_train, X_valid, y_train, y_valid 
    gc.collect()

  except func_timeout.FunctionTimedOut:
    # освободим память от "тяжелых" и ненужных файлов
    del X_train_balanced, y_train_balanced
    gc.collect()

    # обьявим метрики пустыми значениями
    roc_train = 0
    roc_valid = 0
    f1_score = 0
    recall_1 = 0
    precision_1 = 0
    pass

  return roc_train, roc_valid, f1_score, recall_1, precision_1

In [1526]:
# cоздаем объект исследования
# чтобы модель не переобучалась минимизируем roc_train 
# и максимизируем roc_valid
optuna_study_hsbs = optuna.create_study(study_name='HistGradientBoostingClassifier_'+feature_space+'_torow', 
                               directions=['maximize','maximize','maximize','maximize','maximize'], 
                               sampler=optuna.samplers.TPESampler(),
                               pruner='Hyperband',
                               storage='sqlite:///optuna_studies.db',
                               load_if_exists=True)

# ну случай удаления обучения
# optuna.delete_study(study_name='HistGradientBoostingClassifier_'+feature_space+'_torow', storage='sqlite:///optuna_studies.db')

[I 2025-04-19 12:11:38,641] Using an existing study with name 'HistGradientBoostingClassifier_late_torow' instead of creating a new one.


In [190]:
# ищем лучшую комбинацию гиперпараметров n_trials раз
optuna_study_hsbs.optimize(optuna_hgbc, n_trials=300)

[I 2025-04-17 11:47:59,554] Trial 0 finished with values: [0.61122492900589, 0.6092887118668502, 0.03514817367332874, 0.02037554934079105, 0.12781954887218044] and parameters: {'learning_rate': 0.475178349359828, 'max_iter': 132, 'max_leaf_nodes': 16, 'max_depth': 3, 'min_samples_leaf': 15, 'max_features': 0.7554319931897897, 'l2_regularization': 0.24187155144676079, 'class_0_weight': 0.9317956928906831, 'class_1_weight': 0.07913789982470662, 'n_last': 13, 'class_1_percent': 0.6725369170262377, 'random_state': 894926}.
[I 2025-04-17 11:48:04,360] Trial 1 finished with values: [0.6283328074745479, 0.6179523173149353, 0.0007955449482895784, 0.00039952057530962844, 0.09090909090909091] and parameters: {'learning_rate': 0.42070907834199983, 'max_iter': 126, 'max_leaf_nodes': 21, 'max_depth': 12, 'min_samples_leaf': 46, 'max_features': 0.26448224709466295, 'l2_regularization': 0.22030128435769544, 'class_0_weight': 0.663910495859452, 'class_1_weight': 0.45456142566956775, 'n_last': 14, 'cla

In [1527]:
# из полученного результат соврмируем Data Frame
optuna_study_hsbs_pd = optuna_study_hsbs.trials_dataframe()
# переименуем столбы
optuna_study_hsbs_pd.rename(columns={
    'values_0': 'roc_train',
    'values_1': 'roc_valid',
    'values_2': 'f1_score',
    'values_3': 'recall_1',
    'values_4': 'precision_1'
},inplace=True)
# Выделим время потраченное на обучение модели
last_trail = optuna_study_hsbs_pd['number'].max()
optuna_study_hsbs_pd.tail(5)


number  roc_train  roc_valid  f1_score  recall_1  precision_1  \
295     295   0.616471   0.619277  0.067879  1.000000     0.035132   
296     296   0.629472   0.617012  0.070860  0.051538     0.113357   
297     297   0.632912   0.622210  0.090682  0.586496     0.049140   
298     298   0.647337   0.615599  0.066976  0.051938     0.094271   
299     299   0.633097   0.622787  0.074765  0.876149     0.039048   

                datetime_start          datetime_complete  \
295 2025-04-17 12:22:39.182896 2025-04-17 12:22:49.887565   
296 2025-04-17 12:22:49.893908 2025-04-17 12:22:57.113466   
297 2025-04-17 12:22:57.120237 2025-04-17 12:23:06.687695   
298 2025-04-17 12:23:06.694009 2025-04-17 12:23:16.264324   
299 2025-04-17 12:23:16.270128 2025-04-17 12:23:25.954680   

                  duration  params_class_0_weight  ...  \
295 0 days 00:00:10.704669               0.010045  ...   
296 0 days 00:00:07.219558               0.523103  ...   
297 0 days 00:00:09.567458               0.052483  ...   
298 0 days 00:00:09.570315               0.091813  ...   
299 0 days 00:00:09.684552               0.032050  ...   

     params_l2_regularization  params_learning_rate  params_max_depth  \
295                  0.413275              0.229817                 5   
296                  0.402419              0.268199                10   
297                  0.398561              0.212918                 7   
298                  0.066455              0.416087                11   
299                  0.395853              0.291428                 6   

     params_max_features  params_max_iter  params_max_leaf_nodes  \
295             0.191990              207                      7   
296             0.648180              144                     49   
297             0.144793               97                     50   
298             0.555348              271                     46   
299             0.252892              246                     48   

     params_min_samples_leaf  params_n_last  params_random_state     state  
295                        6             11               440145  COMPLETE  
296                        6             15               783038  COMPLETE  
297                        9             24               113511  COMPLETE  
298                        5             17               807128  COMPLETE  
299                        7             25                58302  COMPLETE  

[5 rows x 22 columns]

In [1528]:
# покаждем статистику обучения
print('Максимальное значение метрики ROC AUC на валидационном наборе:',round(optuna_study_hsbs_pd['roc_valid'].max(),3))
print('Среднее значение метрики ROC AUC на валидационном наборе:',round(optuna_study_hsbs_pd['roc_valid'].mean(),3))
print('Максимальное значение метрики f1_score на валидационном наборе:',round(optuna_study_hsbs_pd['f1_score'].max(),3))
print('Среднее значение метрики f1_score на валидационном наборе:',round(optuna_study_hsbs_pd['f1_score'].mean(),3))
print('Максимальное значение метрики recall_1 на валидационном наборе:',round(optuna_study_hsbs_pd['recall_1'].max(),3))
print('Среднее значение метрики recall_1 на валидационном наборе:',round(optuna_study_hsbs_pd['recall_1'].mean(),3))
print('Максимальное значение метрики precision_1 на валидационном наборе:',round(optuna_study_hsbs_pd['precision_1'].max(),3))
print('Среднее значение метрики precision_1 на валидационном наборе:',round(optuna_study_hsbs_pd['precision_1'].mean(),3))

Максимальное значение метрики ROC AUC на валидационном наборе: 0.625
Среднее значение метрики ROC AUC на валидационном наборе: 0.618
Максимальное значение метрики f1_score на валидационном наборе: 0.112
Среднее значение метрики f1_score на валидационном наборе: 0.068
Максимальное значение метрики recall_1 на валидационном наборе: 1.0
Среднее значение метрики recall_1 на валидационном наборе: 0.456
Максимальное значение метрики precision_1 на валидационном наборе: 0.5
Среднее значение метрики precision_1 на валидационном наборе: 0.073


In [1531]:
# Построим зависимость метрик качества модели от number

fig = px.scatter(
    data_frame=optuna_study_hsbs_pd[(optuna_study_hsbs_pd['roc_valid']>=0.99*(optuna_study_hsbs_pd['roc_valid'].max()))&
                                    (optuna_study_hsbs_pd['f1_score']>=0.99*(optuna_study_hsbs_pd['f1_score'].max())) ],
    x='number', #ось абсцисс
    y=['roc_valid','roc_train','precision_1','recall_1','f1_score'], #ось ординат
)
fig.update_layout(
    title ={
        'text':'Зависимость метрик качества модели от number', # Имя рабочей плоскости
        'font':{'size':35,'family':"Times New Roman"}, # размер и стиль написания имени рабочей плоскости
        'x':0.5, # Смешение имени по оси "x" на половину рабочей плоскости
        },
    height =800,# Высота рабочей плоскости
    width = 1350, # Ширина рабочей плоскости
    bargap=0.2, # Добавил расстояния между столбами гистограммы
    xaxis_title='Величина метрики ROC Valid',
    yaxis_title='Величина параметра')
fig.update_xaxes(showspikes=True)
fig.update_yaxes(showspikes=True)

fig.show()

<span style="color:Blue">

Вывод:  

Их всех выбираем точку $number =76$.   
В этой точке оптимальные значения метрик $recall_1$ и $precision_1$, а  
также относительно высокая метрика $ROC AUC$.   
Посмотрим каким значениям гиперпараметров соотвествует выбранная точка.

In [1532]:
# определим номер лучшге варианта
best_optuna_number = 76

# сформируем словарь лучших гипирпарметров RandomForestClassifier
best_param_rf = {
    'learning_rate' : optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_learning_rate'].iloc[0],
    'max_iter' : optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_max_iter'].iloc[0],
    'max_leaf_nodes' : optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_max_leaf_nodes'].iloc[0],
    'max_depth' : optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_max_depth'].iloc[0],
    'min_samples_leaf' : optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_min_samples_leaf'].iloc[0],
    'max_features' : optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_max_features'].iloc[0],
    'l2_regularization' : optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_l2_regularization'].iloc[0],
    'class_weight' : {0: optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_class_0_weight'].iloc[0],
                      1: optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_class_1_weight'].iloc[0],}
    }

# определим перменные для лучших значений параметров
best_n_last = optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_n_last'].iloc[0]
best_class_1_percent = optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_class_1_percent'].iloc[0]
best_random_state = optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_random_state'].iloc[0]


# Выведем принятые наилучшие праметры
print('best learning rate:',round(best_param_rf['learning_rate'],3))
print('best max iter:',best_param_rf['max_iter'])
print('best max leaf nodes:',best_param_rf['max_leaf_nodes'])
print('best max depth:',best_param_rf['max_depth'])
print('best min samples leaf:',best_param_rf['min_samples_leaf'])
print('best max features:',round(best_param_rf['max_features'],3))
print('best l2 regularization:',round(best_param_rf['l2_regularization'],3))
print('best class 0 weight:',round(best_param_rf['class_weight'][0],3))
print('best class 1 weight:',round(best_param_rf['class_weight'][1],3))

print('best class 1 percent:',round(best_class_1_percent,3))
print('best n last:',best_n_last)
print('best random state:',best_random_state)
print('time for best train:',round(optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['duration'].iloc[0].seconds/60),'minutes')

print()
print('ROC AUC на обучающем наборе:', round(optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['roc_train'].iloc[0],3))
print('ROC AUC на валидационном наборе:', round(optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['roc_valid'].iloc[0],3))
print('precision класса 1:', round(optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['precision_1'].iloc[0],3))
print('recall класса 1:', round(optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['recall_1'].iloc[0],3))

best learning rate: 0.291
best max iter: 216
best max leaf nodes: 20
best max depth: 7
best min samples leaf: 6
best max features: 0.218
best l2 regularization: 0.399
best class 0 weight: 0.014
best class 1 weight: 0.142
best class 1 percent: 0.063
best n last: 23
best random state: 118939
time for best train: 0 minutes

ROC AUC на обучающем наборе: 0.628
ROC AUC на валидационном наборе: 0.622
precision класса 1: 0.075
recall класса 1: 0.216


##### <span style="color:MediumSlateBlue">Обучение модели с лучшими параметрами</span>

In [1533]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'late'
count_features = dict_spaces[feature_space]

# с помощью функции features_from_transform_data_torow извлечем  
# из данных transform_data_torow
# признаки сооствествующие n_last последним клиенским операциям
list_n_last_features = features_from_transform_data_torow(best_n_last,count_features,25)

# загружаем обучующие наборы
X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)

# подготовим данные для обучения модели
# с помощью функции class_1_percent_samples зададим долю класса 1
list_c1_percent_id = class_1_percent_samples(y_train_pd,best_class_1_percent,random_state=best_random_state)[:1000000]

# сформируем данные для обучения модели
X_train_balanced = np.array(X_train_pd.loc[list_c1_percent_id])[:,list_n_last_features]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

# освободим память от "тяжелых" и ненужных файлов
del X_train_pd, y_train_pd
gc.collect()


# обучаем модель HistGradientBoostingClassifier с наилучшеми параметрами
gradient_boosting = HistGradientBoostingClassifier(
        **best_param_rf,
        random_state=42)
gradient_boosting.fit(X_train_balanced,y_train_balanced)

# освободим память от "тяжелых" и ненужных файлов
del X_train_balanced, y_train_balanced
gc.collect()

# подгружаем данные для тестирования
X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()[:,list_n_last_features]
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()[:,list_n_last_features]
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_gb__pred_proba = gradient_boosting.predict_proba(X_train)[:,1]
y_valid_gb_pred_proba = gradient_boosting.predict_proba(X_valid)[:,1]

# Делаем предсказание для валидационной выборки
y_valid_gb_pred = gradient_boosting.predict(X_valid)

# освободим память от "тяжелых" и ненужных файлов
del X_train, X_valid
gc.collect()

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_gb__pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_gb_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_gb_pred,zero_division=0))

# time: 2m 30s

ROC AUC на обучающем наборе 0.628
ROC AUC на валидационном наборе 0.622
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.97      0.90      0.94     68747
           1       0.08      0.22      0.11      2503

    accuracy                           0.88     71250
   macro avg       0.52      0.56      0.52     71250
weighted avg       0.94      0.88      0.91     71250



### <span style="color:RoyalBlue">Построение модели на сбалансированных данных подпространства credit torow</span>

#### <span style="color:MediumBlue">Построение модели Logistic Regression</span>

##### <span style="color:MediumSlateBlue">Формирование данных для обучения</span>

Анализ исходных данных, в частности target, показал что представленные данные   
имееют перекос: 96% клиентов у которых не случился дефолт (flag = 0),    
против 4 % - для которых произошел дефолт (flag = 1).  
С помощью функции class_1_percent_samples, сформируем сбаланисрованную выборку  
для обучения моделей.
За основу сбалансировных данных возьмем данные клиентов с дефолтом  
и к ним будем добирать необходимое количество клиентов до сбалансированности. 


Функция class_1_percent_samples принемает две переменные:
- target_data - массив с id и целевой переменной
- class_1_percent - процент класса 1 в результирующем массиве

In [1350]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'credit'
count_features = dict_spaces[feature_space]

In [1351]:
# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

In [1352]:
# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)
y_train_pd.head(4)

id  flag
id                    
1825800  1825800     0
2166483  2166483     0
2534345  2534345     0
1803283  1803283     0

In [1353]:
# взглянем на сблансиорованность данных в y_train
y_train_pd['flag'].value_counts(normalize=True)

flag
0    0.964242
1    0.035758
Name: proportion, dtype: float64

In [1354]:
# сбалансируем данные в y_train_pd
list_c1_percent_id = class_1_percent_samples(y_train_pd,0.5)
# list_c1_percent_features - список 'id' из y_train_pd соотвествующих  
# заданному проценту класса 1
len(list_c1_percent_id)

45860

In [1355]:
# проверим сбалансированность полученного y_train
y_train_pd.loc[list_c1_percent_id]['flag'].value_counts(normalize=True)

flag
1    0.5
0    0.5
Name: proportion, dtype: float64

*transform_data_torow*, показываеются последние N операций клиента.  
В данных в *date_torow*, собраны последние 25 операций клиентов.

Предварительный анализ показывает, что медиальное значение количества клиентских  
операций равно 7. Поэтому, для начала, будем показывать моделе $n_{last} = 7$   
последних клиентских операций.

Для извлечения из *transform_data_torow_25* необходимого количества последних клиенских  
операций ($n_{last}$) используем функцию features_from_transform_data_torow.

Функция features_from_transform_data_torow примает следующие аргументы:
- $n_{last} = 7$ - необходимое количество последних клиентских операций; 
- $n_{groups} = 8$ - количество признаков в $date$ $features$;
- $N_{last} = 25$ - количество $n_{last}$ операций, показанных в transform_data_torow_25


In [1356]:
# с помощью функции features_from_transform_data_torow извлечем  
# из данных transform_data_torow_25
# признаки сооствествующие 7 последним клиенским операциям
list_n_last_features = features_from_transform_data_torow(7,count_features,25)

In [1357]:
# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']
# сформируем данные для проверики модели
X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

In [1358]:
# посмотрим на структуру данных в X_train_balanced
X_train_balanced.head(2)

f1  f2  f3  f4  f5  f6  f7  f8  f9  f10  ...  f91  f92  f93  f94  \
id                                                ...                       
2335465   0  16  11  19  16   0   6  19  19    6  ...    7    2    0    0   
390270   10   5  19  12  13   2   0   0   0    0  ...    0    0    0    0   

         f95  f96  f97  f98  f99  f100  
id                                      
2335465    0    0    0    0    0     0  
390270     0    0    0    0    0     0  

[2 rows x 100 columns]

In [1359]:
# посмотрим на структуру данных в y_train_balanced
y_train_balanced.head(2)

id
2335465    1
390270     1
Name: flag, dtype: int64

In [1360]:
# проверим что выборки действительно совпадают по id
X_train_balanced.index.to_list() == y_train_balanced.index.to_list()

True

##### <span style="color:MediumSlateBlue">Baseline обучение модели LogisticRegression</span>

In [1361]:
# обучаем модель логистической регрессии
logistic_regression = linear_model.LogisticRegression(random_state=42, max_iter=10000)
logistic_regression.fit(np.array(X_train_balanced)[:,list_n_last_features],np.array(y_train_balanced))

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_LR_pred_proba = logistic_regression.predict_proba(X_train[:,list_n_last_features])[:,1]
y_valid_LR_pred_proba = logistic_regression.predict_proba(X_valid[:,list_n_last_features])[:,1]

# Делаем предсказание для валидационной выборки
y_valid_LR_pred = logistic_regression.predict(X_valid[:,list_n_last_features])

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_LR_pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_LR_pred_proba),3))

print('Основные метрики на тестовом наборе:')
print(metrics.classification_report(y_valid,y_valid_LR_pred))

# time: 1m 12s

ROC AUC на обучающем наборе 0.552
ROC AUC на валидационном наборе 0.555
Основные метрики на тестовом наборе:
              precision    recall  f1-score   support

           0       0.97      0.52      0.68     68747
           1       0.04      0.55      0.08      2503

    accuracy                           0.53     71250
   macro avg       0.50      0.54      0.38     71250
weighted avg       0.94      0.53      0.66     71250



##### <span style="color:MediumSlateBlue">Анализ влияния scaler преобразования на качество и скорость схождения модели</span>

In [221]:
# формируем список из необходимых scaler
scalers = [MinMaxScaler(),RobustScaler() ,StandardScaler()]

# сформируем списко для заполнения данными результатов анализа
scalers_data = []

# установим ограничение на время обучения модели в 600 секунд (10 минут)
time_out = 600

for scaler in scalers:
        # для того чтобы следить за выполнением цикла введем индикатор
        print('current scaler: ', scaler)

         # сформируем список для заполнения данными текушего scaler
        current_scaler_data = [scaler]
        
        # выполним scaler преобразование
        X_train_s_balanced = scaler.fit_transform(np.array(X_train_balanced)[:,list_n_last_features])
        X_train_s = scaler.transform(X_train[:,list_n_last_features])
        X_valid_s = scaler.transform(X_valid[:,list_n_last_features])

        try:
                # для модуля func_time_out упакуем обучение модели в функцию try_func
                def try_func():
                        logistic_regression = linear_model.LogisticRegression(random_state=42, max_iter=10000)
                        return logistic_regression.fit(X_train_s_balanced,y_train_balanced)
                    
                # фиксируем время начала
                start_time = time.time()
                
                # запускаем обучение модели с ограничением по времени
                logistic_regression = func_timeout.func_timeout(time_out, try_func)
                
                # фиксируем время окончания обучения
                end_time = time.time()
                
                # запишем время обучения модели
                current_scaler_data.append(round(end_time-start_time))

                # Делаем предсказание для обучающей и валидационной выборки
                y_valid_lr_pred = logistic_regression.predict(X_valid_s)
                
                # для метрик ROC AUC делаем предсказание модели для обучающей и валидационной выборки  
                # в виде вероятности принадлежности к классу 1 
                y_train_lr_pred_proba = logistic_regression.predict_proba(X_train_s)[:,1]
                y_valid_lr_pred_proba = logistic_regression.predict_proba(X_valid_s)[:,1]

                #Считаем метрики ROC AUC yна обуающем и валидационном наборе и добавляем их в спискок
                current_scaler_data.append(round(metrics.roc_auc_score(y_train, y_train_lr_pred_proba),3))
                current_scaler_data.append(round(metrics.roc_auc_score(y_valid, y_valid_lr_pred_proba),3))

                #Считаем метрики для класса 0 на валидационном наборе и добавляем их в список
                current_scaler_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))
                current_scaler_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))


                #Считаем метрики для класса 1 на валидационном набопе и добавляем их в список
                current_scaler_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))
                current_scaler_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))

                # добавляем полученные данные в список scalers_data
                scalers_data.append(current_scaler_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                scaler_pd =pd.DataFrame(
                        columns=['scaler','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = scalers_data)
                # сохраняем dataframe
                scaler_pd.to_csv('data_recovery/scaler_pd.csv',index=False)
               
                # очистим output от прошедшей итерации
                clear_output()

        except func_timeout.FunctionTimedOut:
                # если время обучения привышает лимит
                # запишем в current_scaler_data соотвествующую данные
                current_scaler_data = [scaler,'>30m',0,0,0,0,0,0]
                # добавляем полученные данные в список scalers_data
                scalers_data.append(current_scaler_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                scaler_pd =pd.DataFrame(
                        columns=['scaler','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = scalers_data)
                # сохраняем dataframe
                scaler_pd.to_csv('data_recovery/scaler_pd.csv',index=False)
                
                # очистим output от прошедшей итерации
                clear_output()
                # переходим к следующему scaler
                pass
# очистим output
clear_output()

# сформируем данные соотвествующие лучщему ROC AUC на валидацинном наборе
best_roc_valid_data = scaler_pd[scaler_pd['roc_valid']==scaler_pd['roc_valid'].max()]

# выведем лучший результат на валидационном наборе
print('result:')
print('best scaler on valid:',best_roc_valid_data.iloc[0]['scaler'])
print('ROC AUC on train:', best_roc_valid_data.iloc[0]['roc_train'])
print('ROC AUC on valid:', best_roc_valid_data.iloc[0]['roc_valid'])
print('Time fit for best scaler:', best_roc_valid_data.iloc[0]['time_fit'],' seconds')

# выведем полученный dataframe
scaler_pd

# time: 

result:
best scaler on valid: MinMaxScaler()
ROC AUC on train: 0.552
ROC AUC on valid: 0.554
Time fit for best scaler: 0  seconds


scaler  time_fit  roc_train  roc_valid  recall_0  precision_0  \
0    MinMaxScaler()         0      0.552      0.554     0.531         0.97   
1    RobustScaler()         0      0.552      0.553     0.531         0.97   
2  StandardScaler()         0      0.552      0.553     0.530         0.97   

   recall_1  precision_1  
0     0.545        0.041  
1     0.544        0.041  
2     0.543        0.040

##### <span style="color:MediumSlateBlue"> Анализ влияния solver оптимизатора на качество и скорость обучения модели</span>

Проверим качество и скорость сходимости модели при разных solver  
Проверку осуществим через цикл  
Чтобы модель не сходилась бесконечно с помощью модуля func_timeout  
поставим ограничение времени схождения в 10 минут

In [222]:
# подготовим данные для обучения модели

# обьявим scaler
scaler = StandardScaler()
# выполним scaler преобразование
X_train_s_balanced = scaler.fit_transform(np.array(X_train_balanced)[:,list_n_last_features])
X_train_s = scaler.transform(X_train[:,list_n_last_features])
X_valid_s = scaler.transform(X_valid[:,list_n_last_features])

# time: 10s

In [223]:
# Зададим список solvers
solvers_list = ['lbfgs', 'liblinear', 'newton-cg', 'newton-cholesky', 'sag', 'saga']

# сформируем список для заполнения
solvers_data = []

# установим ограничение на время обучения модели в 300 секунд (5 минут)
time_out = 300

for solver in solvers_list:
        # для того чтобы следить за выполнением цикла введем индикатор
        print('current solver: ', solver)

         # сформируем список для заполнения данными текушего solver
        current_solver_data = [solver]
        
        try:
                # для модуля func_time_out упакуем обучение модели в функцию try_func
                def try_func():
                        logistic_regression = linear_model.LogisticRegression(solver= solver,
                                                                  random_state=42, 
                                                                  max_iter=10000)
                        return logistic_regression.fit(X_train_s_balanced,y_train_balanced)
                    
                # фиксируем время начала
                start_time = time.time()
                
                # запускаем обучение модели с ограничением по времени
                logistic_regression = func_timeout.func_timeout(time_out, try_func)
                
                # фиксируем время окончания обучения
                end_time = time.time()
                
                # запишем время обучения модели
                current_solver_data.append(round(end_time-start_time))

                # Делаем предсказание для обучающей и валидационной выборки
                y_valid_lr_pred = logistic_regression.predict(X_valid_s)
                
                # для метрик ROC AUC делаем предсказание модели для обучающей и валидационной выборки  
                # в виде вероятности принадлежности к классу 1 
                y_train_lr_pred_proba = logistic_regression.predict_proba(X_train_s)[:,1]
                y_valid_lr_pred_proba = logistic_regression.predict_proba(X_valid_s)[:,1]

                #Считаем метрики ROC AUC yна обуающем и валидационном наборе и добавляем их в спискок
                current_solver_data.append(round(metrics.roc_auc_score(y_train, y_train_lr_pred_proba),3))
                current_solver_data.append(round(metrics.roc_auc_score(y_valid, y_valid_lr_pred_proba),3))

                #Считаем метрики для класса 0 на валидационном наборе и добавляем их в список
                current_solver_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))
                current_solver_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))


                #Считаем метрики для класса 1 на валидационном набопе и добавляем их в список
                current_solver_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))
                current_solver_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))

                # запишем данные полученные на одной итерации
                solvers_data.append(current_solver_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                solvers_pd =pd.DataFrame(
                        columns=['solver','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = solvers_data)
                # сохраняем dataframe
                solvers_pd.to_csv('data_recovery/solvers_pd.csv',index=False)
               
                # очистим output от прошедшей итерации
                clear_output()

        except func_timeout.FunctionTimedOut:
                # если время обучения привышает лимит
                # запишем в current_solver_data соотвествующую данные
                current_solver_data = [solver,'>10m',0,0,0,0,0,0]
                # добавляем полученные данные в список solvers_data
                solvers_data.append(current_solver_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                solvers_pd =pd.DataFrame(
                        columns=['solver','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = solvers_data)
                # сохраняем dataframe
                solvers_pd.to_csv('data_recovery/solvers_pd.csv',index=False)
                
                # очистим output от прошедшей итерации
                clear_output()
                # переходим к следующему solver
                pass
# очистим output
clear_output()

# сформируем данные соотвествующие лучщему ROC AUC на валидацинном наборе
best_roc_valid_data = solvers_pd[solvers_pd['roc_valid']==solvers_pd['roc_valid'].max()]

# выведем лучший результат на валидационном наборе
print('result:')
print('best solver on valid:',best_roc_valid_data.iloc[0]['solver'])
print('ROC AUC on train:', best_roc_valid_data.iloc[0]['roc_train'])
print('ROC AUC on valid:', best_roc_valid_data.iloc[0]['roc_valid'])
print('Time fit for best solver:', best_roc_valid_data.iloc[0]['time_fit'],' seconds')

# выведем полученный dataframe
solvers_pd

# time: 11m 35s

result:
best solver on valid: lbfgs
ROC AUC on train: 0.552
ROC AUC on valid: 0.553
Time fit for best solver: 0  seconds


solver  time_fit  roc_train  roc_valid  recall_0  precision_0  \
0            lbfgs         0      0.552      0.553      0.53         0.97   
1        liblinear         0      0.552      0.553      0.53         0.97   
2        newton-cg         0      0.552      0.553      0.53         0.97   
3  newton-cholesky         0      0.552      0.553      0.53         0.97   
4              sag         0      0.552      0.553      0.53         0.97   
5             saga         0      0.552      0.553      0.53         0.97   

   recall_1  precision_1  
0     0.543         0.04  
1     0.543         0.04  
2     0.544         0.04  
3     0.543         0.04  
4     0.543         0.04  
5     0.543         0.04

##### <span style="color:MediumSlateBlue">Подбор гиперпараметров модели</span>

In [1534]:
# для выбора sceler преобразвания на понадобится словарь
dict_scalers ={
    'MinMaxScaler':MinMaxScaler(),
    'RobustScaler':RobustScaler(),
    'StandardScaler':StandardScaler(),
}
# определим пространство признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'credit'
count_features = dict_spaces[feature_space]

# настроим оптимизацию гипер параметров
def optuna_lg(trial):
  # задаем пространства поиска гиперпараметров
  C = trial.suggest_float('C',0.01,1)
  solver = trial.suggest_categorical('solver', ['lbfgs', 'liblinear', 'newton-cg', 'newton-cholesky'])
  class_0_weight = trial.suggest_float('class_0_weight',0.01,1)
  class_1_weight = trial.suggest_float('class_1_weight',0.01,1)
  n_last = trial.suggest_int('n_last', 10, 25,step = 1)
  class_1_percent = trial.suggest_float('class_1_percent',0.01,1)
  scaler = trial.suggest_categorical('scaler', ['MinMaxScaler', 'RobustScaler','StandardScaler'])
  random_state = trial.suggest_int('random_state', 1, 1000000)

  # создаем модель
  optuna_log_reg = linear_model.LogisticRegression(
      solver=solver,
      C=C,
      class_weight={0:class_0_weight,1:class_1_weight},
      random_state=random_state,
      max_iter=10000)

  # с помощью функции features_from_transform_data_torow извлечем  
  # из данных transform_data_torow
  # признаки сооствествующие n_last последним клиенским операциям
  list_n_last_features = features_from_transform_data_torow(n_last,count_features,25)

  # обьявим scaler
  scaler = dict_scalers[scaler]

  # загружаем обучующие наборы
  X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
  y_train_pd = pd.read_csv('target/target_train.csv')

  # поготовим данные y_train_pd к работе с функцией class_1_percent_samples
  y_train_pd.set_index('id',drop=False,inplace=True)

  # подготовим данные для обучения модели
  # с помощью функции class_1_percent_samples зададим долю 
  # класса 1
  list_c1_percent_id = class_1_percent_samples(y_train_pd,class_1_percent,random_state=random_state)[:1000000]

  # сформируем данные для обучения базовой модели
  X_train_s_balanced = scaler.fit_transform(np.array(X_train_pd.loc[list_c1_percent_id])[:,list_n_last_features])
  y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

  # освободим память от "тяжелых" и ненужных файлов
  del X_train_pd, y_train_pd
  gc.collect()

  # я не воспользовался параметром timeout метода optimize потому, что  
  # optimize отставливает поиск параметров, если время обучения 
  # превышает timeout. Мне нужно чтобы поиск параметров продолжился.
  try:
    # для модуля func_time_out упакуем обучение модели в функцию try_func
    def try_func():
            return optuna_log_reg.fit(X_train_s_balanced, y_train_balanced)
    # обучаем модель с ограничением по времени 10 минут (600 секунд)
    optuna_log_reg = func_timeout.func_timeout(600, try_func)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train_s_balanced,y_train_balanced
    gc.collect()

    # подгружаем данные для тестирования
    X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()[:,list_n_last_features]
    y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
    X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()[:,list_n_last_features]
    y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

    # сформируем данные для проверки модели
    X_train_s = scaler.transform(X_train)
    X_valid_s = scaler.transform(X_valid)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train, X_valid
    gc.collect()

    # делаем предсказание на обучающем и валидационном наборе и считаем метрики
    roc_train = metrics.roc_auc_score(y_train, optuna_log_reg.predict_proba(X_train_s)[:,1])
    roc_valid = metrics.roc_auc_score(y_valid, optuna_log_reg.predict_proba(X_valid_s)[:,1])
    f1_score = metrics.f1_score(y_valid, optuna_log_reg.predict(X_valid_s))
    recall_1 = metrics.recall_score(y_valid, optuna_log_reg.predict(X_valid_s),average=None,zero_division=0)[1]
    precision_1 = metrics.precision_score(y_valid, optuna_log_reg.predict(X_valid_s),average=None,zero_division=0)[1]

    del X_train_s, X_valid_s, y_train, y_valid
    gc.collect()

  except func_timeout.FunctionTimedOut:
    # освободим память от "тяжелых" и ненужных файлов
    del X_train_s_balanced, y_train_balanced
    gc.collect()

    # обьявим метрики пустыми значениями
    roc_train = 0
    roc_valid = 0
    f1_score = 0
    recall_1 = 0
    precision_1 = 0
    pass

  return roc_train, roc_valid, f1_score, recall_1, precision_1

In [1535]:
# cоздаем объект исследования
# чтобы модель не переобучалась минимизируем roc_train 
# и максимизируем roc_valid
optuna_study_lg = optuna.create_study(study_name='LogisticRegression_'+feature_space+'_torow', 
                               directions=['maximize','maximize','maximize','maximize','maximize'], 
                               sampler=optuna.samplers.TPESampler(),
                               pruner='Hyperband',
                               storage='sqlite:///optuna_studies.db',
                               load_if_exists=True)
# на случай удаления 
# optuna.delete_study(study_name='LogisticRegression_'+feature_space+'_torow', storage='sqlite:///optuna_studies.db')

[I 2025-04-19 14:04:36,123] Using an existing study with name 'LogisticRegression_credit_torow' instead of creating a new one.


In [226]:
# ищем лучшую комбинацию гиперпараметров n_trials раз
optuna_study_lg.optimize(optuna_lg, n_trials=300)

[I 2025-04-17 12:24:02,959] Trial 0 finished with values: [0.5561232639889063, 0.5580969701821035, 0.06784304683367468, 0.9992009588493808, 0.03511358211888917] and parameters: {'C': 0.9276114499257361, 'solver': 'newton-cg', 'class_0_weight': 0.3224128143469186, 'class_1_weight': 0.9687038417932073, 'n_last': 21, 'class_1_percent': 0.45538165981186396, 'scaler': 'StandardScaler', 'random_state': 225799}.
[I 2025-04-17 12:24:05,369] Trial 1 finished with values: [0.5544812942059225, 0.548252237393967, 0.06787520507640367, 1.0, 0.03512982456140351] and parameters: {'C': 0.6709328243609084, 'solver': 'liblinear', 'class_0_weight': 0.27245842961844896, 'class_1_weight': 0.49434241552299996, 'n_last': 20, 'class_1_percent': 0.6359074544046418, 'scaler': 'MinMaxScaler', 'random_state': 235292}.
[I 2025-04-17 12:24:07,973] Trial 2 finished with values: [0.556314624276002, 0.5569850573539864, 0.0, 0.0, 0.0] and parameters: {'C': 0.09352949097354249, 'solver': 'newton-cg', 'class_0_weight': 0.

In [1536]:
# из полученного результат соврмируем Data Frame
optuna_study_lg_pd = optuna_study_lg.trials_dataframe().dropna()
# переименуем столбы
optuna_study_lg_pd.rename(columns={
    'values_0': 'roc_train',
    'values_1': 'roc_valid',
    'values_2': 'f1_score',
    'values_3': 'recall_1',
    'values_4': 'precision_1'
},inplace=True)
# Выделим время потраченное на обучение модели
optuna_study_lg_pd.head(5)

number  roc_train  roc_valid  f1_score  recall_1  precision_1  \
0       0   0.556123   0.558097  0.067843  0.999201     0.035114   
1       1   0.554481   0.548252  0.067875  1.000000     0.035130   
2       2   0.556315   0.556985  0.000000  0.000000     0.000000   
3       3   0.555398   0.550849  0.073683  0.649221     0.039058   
4       4   0.556657   0.558328  0.067875  1.000000     0.035130   

              datetime_start          datetime_complete  \
0 2025-04-17 12:24:00.234068 2025-04-17 12:24:02.957207   
1 2025-04-17 12:24:02.963000 2025-04-17 12:24:05.366108   
2 2025-04-17 12:24:05.373426 2025-04-17 12:24:07.971284   
3 2025-04-17 12:24:07.976347 2025-04-17 12:24:10.352777   
4 2025-04-17 12:24:10.359292 2025-04-17 12:24:12.843306   

                duration  params_C  params_class_0_weight  \
0 0 days 00:00:02.723139  0.927611               0.322413   
1 0 days 00:00:02.403108  0.670933               0.272458   
2 0 days 00:00:02.597858  0.093529               0.650147   
3 0 days 00:00:02.376430  0.973495               0.168199   
4 0 days 00:00:02.484014  0.854215               0.087206   

   params_class_1_percent  params_class_1_weight  params_n_last  \
0                0.455382               0.968704             21   
1                0.635907               0.494342             20   
2                0.427037               0.344732             22   
3                0.590170               0.122340             22   
4                0.357242               0.560534             25   

   params_random_state   params_scaler    params_solver     state  
0               225799  StandardScaler        newton-cg  COMPLETE  
1               235292    MinMaxScaler        liblinear  COMPLETE  
2               304639    RobustScaler        newton-cg  COMPLETE  
3               872364  StandardScaler            lbfgs  COMPLETE  
4               999843    MinMaxScaler  newton-cholesky  COMPLETE

In [1537]:
# покаждем статистику обучения
print('Максимальное значение метрики ROC AUC на валидационном наборе:',round(optuna_study_lg_pd['roc_valid'].max(),3))
print('Среднее значение метрики ROC AUC на валидационном наборе:',round(optuna_study_lg_pd['roc_valid'].mean(),3))
print('Максимальное значение метрики f1_score на валидационном наборе:',round(optuna_study_lg_pd['f1_score'].max(),3))
print('Среднее значение метрики f1_score на валидационном наборе:',round(optuna_study_lg_pd['f1_score'].mean(),3))
print('Максимальное значение метрики recall_1 на валидационном наборе:',round(optuna_study_lg_pd['recall_1'].max(),3))
print('Среднее значение метрики recall_1 на валидационном наборе:',round(optuna_study_lg_pd['recall_1'].mean(),3))
print('Максимальное значение метрики precision_1 на валидационном наборе:',round(optuna_study_lg_pd['precision_1'].max(),3))
print('Среднее значение метрики precision_1 на валидационном наборе:',round(optuna_study_lg_pd['precision_1'].mean(),3))

Максимальное значение метрики ROC AUC на валидационном наборе: 0.559
Среднее значение метрики ROC AUC на валидационном наборе: 0.555
Максимальное значение метрики f1_score на валидационном наборе: 0.08
Среднее значение метрики f1_score на валидационном наборе: 0.05
Максимальное значение метрики recall_1 на валидационном наборе: 1.0
Среднее значение метрики recall_1 на валидационном наборе: 0.487
Максимальное значение метрики precision_1 на валидационном наборе: 0.067
Среднее значение метрики precision_1 на валидационном наборе: 0.031


In [1540]:
# Визуализируем метрики полученные при optuna оптимизации
fig = px.scatter(
    data_frame=optuna_study_lg_pd[(optuna_study_lg_pd['roc_valid']>0.997*optuna_study_lg_pd['roc_valid'].max())&
                                (optuna_study_lg_pd['f1_score']>0.9*optuna_study_lg_pd['f1_score'].max())],
    x='number', #ось абсцисс
    y=['roc_train','roc_valid','recall_1','precision_1','f1_score'], #ось ординат
)
fig.update_layout(
    title ={
        'text':'Зависимость качества модели от trials optuna', # Имя рабочей плоскости
        'font':{'size':35,'family':"Times New Roman"}, # размер и стиль написания имени рабочей плоскости
        'x':0.5, # Смешение имени по оси "x" на половину рабочей плоскости
        },
    height =800,# Высота рабочей плоскости
    width = 1350, # Ширина рабочей плоскости
    bargap=0.2, # Добавил расстояния между столбами гистограммы
    xaxis_title='trials optuna',
    yaxis_title='Величина метрики')
fig.update_xaxes(showspikes=True)
fig.update_yaxes(showspikes=True)

fig.show()

<span style="color:Blue">

Вывод:  

Их всех выбираем точку $number =48$.   
В этой точке одно из самых больших значений $ROC AUC$.  
Посмотрим каким значениям гиперпараметров соотвествует выбранная точка.

In [1541]:
# определим номер лучшге варианта
best_optuna_number = 48

# сформируем словарь лучших гипирпарметров RandomForestClassifier
best_param_lr_torow = {
    'C' : round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_C'].iloc[0],3),
    'class_weight' : {0:round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_class_0_weight'].iloc[0],3),
                      1:round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_class_1_weight'].iloc[0],3)},
    }
# создадим перменные
best_n_last = int(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_n_last'].iloc[0])
best_scaler = optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_scaler'].iloc[0]
best_class_1_percent = optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_class_1_percent'].iloc[0]
best_random_state = int(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_random_state'].iloc[0])
# Выведем принятые наилучшие праметры
print('best C:',best_param_lr_torow['C'])
print('best class 0 weight:',best_param_lr_torow['class_weight'][0])
print('best class 1 weight:',best_param_lr_torow['class_weight'][1])

print('best class 1 percent:',round(best_class_1_percent,3))
print('best scaler:',best_scaler)
print('best n_last:',round(best_n_last,3))
print('best best random state:',best_random_state)
print('time for best train:',round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['duration'].iloc[0].seconds/60),'minutes')

print()
print('ROC AUC на обучающем наборе:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['roc_train'].iloc[0],3))
print('ROC AUC на валидационном наборе:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['roc_valid'].iloc[0],3))
print('precision класса 1:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['precision_1'].iloc[0],3))
print('recall класса 1:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['recall_1'].iloc[0],3))

best C: 0.811
best class 0 weight: 0.393
best class 1 weight: 0.777
best class 1 percent: 0.324
best scaler: MinMaxScaler
best n_last: 22
best best random state: 54651
time for best train: 0 minutes

ROC AUC на обучающем наборе: 0.557
ROC AUC на валидационном наборе: 0.558
precision класса 1: 0.042
recall класса 1: 0.46


##### <span style="color:MediumSlateBlue">Обучение модели с лучшими параметрами</span>

In [1542]:
# для выбора sceler преобразвания на понадобится словарь
dict_scalers ={
    'MinMaxScaler':MinMaxScaler(),
    'RobustScaler':RobustScaler(),
    'StandardScaler':StandardScaler(),
}

# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'credit'
count_features = dict_spaces[feature_space]

# с помощью функции features_from_transform_data_torow извлечем  
# из данных transform_data_torow_25
# признаки сооствествующие n_last последним клиенским операциям
list_n_last_features = features_from_transform_data_torow(best_n_last,count_features,25)

# обьявим scaler
scaler = dict_scalers[best_scaler]

# загружаем обучующие наборы
X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)

# подготовим данные для обучения модели
# с помощью функции class_1_percent_samples зададим долю 
# класса 1
list_c1_percent_id = class_1_percent_samples(y_train_pd,best_class_1_percent,random_state=best_random_state)[:1000000]

# сформируем данные для обучения базовой модели
X_train_s_balanced = scaler.fit_transform(np.array(X_train_pd.loc[list_c1_percent_id])[:,list_n_last_features])
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

# освободим память от "тяжелых" и ненужных файлов
del X_train_pd, y_train_pd
gc.collect()


# обучаем модель LogisticRegression с наилучшеми параметрами
logistic_regression = linear_model.LogisticRegression(
        **best_param_lr_torow,
        random_state=best_random_state,
        max_iter=10000)
logistic_regression.fit(X_train_s_balanced,y_train_balanced)

# удаляем крупные файлы чтобы высвободить память 
del X_train_s_balanced,y_train_balanced
gc.collect()

# подгружаем данные для тестирования
X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()[:,list_n_last_features]
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()[:,list_n_last_features]
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()
    
# сформируем данные для проверки модели
X_train_s = scaler.transform(X_train)
X_valid_s = scaler.transform(X_valid)

# удаляем крупные файлы чтобы высвободить память 
del X_train, X_valid
gc.collect()

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_lr_pred_proba = logistic_regression.predict_proba(X_train_s)[:,1]
y_valid_lr_pred_proba = logistic_regression.predict_proba(X_valid_s)[:,1]

# Делаем предсказание для валидационной выборки
y_valid_lr_pred = logistic_regression.predict(X_valid_s)

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_lr_pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_lr_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_lr_pred,zero_division=0))

# time: 2m 40s

ROC AUC на обучающем наборе 0.557
ROC AUC на валидационном наборе 0.558
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.97      0.62      0.76     68747
           1       0.04      0.46      0.08      2503

    accuracy                           0.62     71250
   macro avg       0.51      0.54      0.42     71250
weighted avg       0.94      0.62      0.73     71250



#### <span style="color:MediumBlue">Построение модели Random Forest Classifier</span>

##### <span style="color:MediumSlateBlue">Формирование данных для обучения</span>

Анализ исходных данных, в частности target, показал что представленные данные   
имееют перекос: 96% клиентов у которых не случился дефолт (flag = 0),    
против 4 % - для которых произошел дефолт (flag = 1).  
С помощью функции class_1_percent_samples, сформируем сбаланисрованную выборку  
для обучения моделей.
За основу сбалансировных данных возьмем данные клиентов с дефолтом  
и к ним будем добирать необходимое количество клиентов до сбалансированности. 


Функция class_1_percent_samples принемает две переменные:
- target_data - массив с id и целевой переменной
- class_1_percent - процент класса 1 в результирующем массиве

In [1364]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'credit'
count_features = dict_spaces[feature_space]

In [1365]:
# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

In [1366]:
# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)
y_train_pd.head(4)

id  flag
id                    
1825800  1825800     0
2166483  2166483     0
2534345  2534345     0
1803283  1803283     0

In [1367]:
# взглянем на сблансиорованность данных в y_train
y_train_pd['flag'].value_counts(normalize=True)

flag
0    0.964242
1    0.035758
Name: proportion, dtype: float64

In [1368]:
# сбалансируем данные в y_train_pd
list_c1_percent_id = class_1_percent_samples(y_train_pd,0.5)
# list_c1_percent_features - список 'id' из y_train_pd соотвествующих  
# заданному проценту класса 1
len(list_c1_percent_id)

45860

In [1369]:
# проверим сбалансированность полученного y_train
y_train_pd.loc[list_c1_percent_id]['flag'].value_counts(normalize=True)

flag
1    0.5
0    0.5
Name: proportion, dtype: float64

*transform_data_torow*, показываеются последние N операций клиента.  
В данных в *date_torow*, собраны последние 25 операций клиентов.

Предварительный анализ показывает, что медиальное значение количества клиентских  
операций равно 7. Поэтому, для начала, будем показывать моделе $n_{last} = 7$   
последних клиентских операций.

Для извлечения из *transform_data_torow_25* необходимого количества последних клиенских  
операций ($n_{last}$) используем функцию features_from_transform_data_torow.

Функция features_from_transform_data_torow примает следующие аргументы:
- $n_{last} = 7$ - необходимое количество последних клиентских операций; 
- $n_{groups} = 8$ - количество признаков в $date$ $features$;
- $N_{last} = 25$ - количество $n_{last}$ операций, показанных в transform_data_torow_25


In [1370]:
# с помощью функции features_from_transform_data_torow извлечем  
# из данных transform_data_torow_25
# признаки сооствествующие 7 последним клиенским операциям
list_n_last_features = features_from_transform_data_torow(7,count_features,25)

In [1371]:
# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']
# сформируем данные для проверики модели
X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

In [1372]:
# посмотрим на структуру данных в X_train_balanced
X_train_balanced.head(2)

f1  f2  f3  f4  f5  f6  f7  f8  f9  f10  ...  f91  f92  f93  f94  \
id                                                ...                       
2335465   0  16  11  19  16   0   6  19  19    6  ...    7    2    0    0   
390270   10   5  19  12  13   2   0   0   0    0  ...    0    0    0    0   

         f95  f96  f97  f98  f99  f100  
id                                      
2335465    0    0    0    0    0     0  
390270     0    0    0    0    0     0  

[2 rows x 100 columns]

In [1373]:
# посмотрим на структуру данных в y_train_balanced
y_train_balanced.head(2)

id
2335465    1
390270     1
Name: flag, dtype: int64

In [1374]:
# проверим что выборки действительно совпадают по id
X_train_balanced.index.to_list() == y_train_balanced.index.to_list()

True

##### <span style="color:MediumSlateBlue">Baseline обучение модели RandomForestClassifier</span>

In [1375]:
# обучаем модель логистической регрессии
# чтобы модель пыталась найти связь во всех признаках
random_forest = RandomForestClassifier(random_state=42, n_jobs=-1)
random_forest.fit(np.array(X_train_balanced)[:,list_n_last_features],np.array(y_train_balanced))

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_rf__pred_proba = random_forest.predict_proba(X_train[:,list_n_last_features])[:,1]
y_valid_rf_pred_proba = random_forest.predict_proba(X_valid[:,list_n_last_features])[:,1]

# Делаем предсказание для валидационной выборки
y_valid_rf_pred = random_forest.predict(X_valid[:,list_n_last_features])

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_rf__pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_rf_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_rf_pred))

# time: 2m 5s

ROC AUC на обучающем наборе 0.967
ROC AUC на валидационном наборе 0.621
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.97      0.64      0.78     68747
           1       0.05      0.52      0.09      2503

    accuracy                           0.64     71250
   macro avg       0.51      0.58      0.43     71250
weighted avg       0.94      0.64      0.75     71250



##### <span style="color:MediumSlateBlue">Подбор гиперпараметров модели</span>

In [1543]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'credit'
count_features = dict_spaces[feature_space]

# настроим оптимизацию гипер параметров
def optuna_rf(trial):
  # задаем пространства поиска гиперпараметров
  # задаем пространства поиска гиперпараметров
  n_estimators = trial.suggest_int('n_estimators', 50, 150,step = 5)
  criterion = trial.suggest_categorical('criterion',['gini', 'entropy', 'log_loss'])
  max_depth = trial.suggest_int('max_depth', 9, 20,step = 1)
  min_samples_split = trial.suggest_int('min_samples_split', 5, 15,step = 1)
  min_samples_leaf = trial.suggest_int('min_samples_leaf', 5, 25,step = 1)
  max_features = trial.suggest_float('max_features',0.1,1)
  max_samples = trial.suggest_float('max_samples',0.1,1)
  class_0_weight = trial.suggest_float('class_0_weight',0.01,1)
  class_1_weight = trial.suggest_float('class_1_weight',0.01,1)
  n_last = trial.suggest_int('n_last', 5, 25,step = 1)
  class_1_percent = trial.suggest_float('class_1_percent',0.01,1)
  random_state = trial.suggest_int('random_state', 1, 1000000)


  # создаем модель
  optuna_random_forest = RandomForestClassifier(
      n_estimators = n_estimators, 
      criterion = criterion,
      max_depth = max_depth,
      min_samples_split = min_samples_split,  
      min_samples_leaf = min_samples_leaf,
      max_features=max_features,
      max_samples=max_samples,
      class_weight={0:class_0_weight,1:class_1_weight},
      n_jobs=-1,
      random_state=random_state)

  # с помощью функции features_from_transform_data_torow извлечем  
  # из данных transform_data_torow
  # признаки сооствествующие n_last последним клиенским операциям
  list_n_last_features = features_from_transform_data_torow(n_last,count_features,25)

  # загружаем обучующие наборы
  X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
  y_train_pd = pd.read_csv('target/target_train.csv')

  # поготовим данные y_train_pd к работе с функцией class_1_percent_samples
  y_train_pd.set_index('id',drop=False,inplace=True)

  # подготовим данные для обучения модели
  # с помощью функции class_1_percent_samples зададим долю 
  # класса 1
  list_c1_percent_id = class_1_percent_samples(y_train_pd,class_1_percent,random_state=random_state)[:1000000]

  # сформируем данные для обучения базовой модели
  X_train_balanced = np.array(X_train_pd.loc[list_c1_percent_id])[:,list_n_last_features]
  y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

  # освободим память от "тяжелых" и ненужных файлов
  del X_train_pd, y_train_pd
  gc.collect()

  # я не воспользовался параметром timeout метода optimize потому, что  
  # optimize отставливает поиск параметров, если время обучения 
  # превышает timeout. Мне нужно чтобы поиск параметров продолжился.
  try:
    # для модуля func_time_out упакуем обучение модели в функцию try_func
    def try_func():
            return optuna_random_forest.fit(X_train_balanced,y_train_balanced)
    # обучаем модель с ограничением по времени 10 минут (600 секунд)
    optuna_random_forest = func_timeout.func_timeout(600, try_func)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train_balanced, y_train_balanced
    gc.collect()

    # подгружаем данные для тестирования
    X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()[:,list_n_last_features]
    y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
    X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()[:,list_n_last_features]
    y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

    # делаем предсказание на обучающем и валидационном наборе и считаем метрики
    roc_train = metrics.roc_auc_score(y_train, optuna_random_forest.predict_proba(X_train)[:,1])
    roc_valid = metrics.roc_auc_score(y_valid, optuna_random_forest.predict_proba(X_valid)[:,1])
    f1_score = metrics.f1_score(y_valid, optuna_random_forest.predict(X_valid))
    recall_1 = metrics.recall_score(y_valid, optuna_random_forest.predict(X_valid),average=None,zero_division=0)[1]
    precision_1 = metrics.precision_score(y_valid, optuna_random_forest.predict(X_valid),average=None,zero_division=0)[1]

    # удаляем крупные файлы чтобы высвободить память 
    del X_train, X_valid, y_train, y_valid 
    gc.collect()

  except func_timeout.FunctionTimedOut:
    # освободим память от "тяжелых" и ненужных файлов
    del X_train_balanced, y_train_balanced
    gc.collect()

    # обьявим метрики пустыми значениями
    roc_train = 0
    roc_valid = 0
    f1_score = 0
    recall_1 = 0
    precision_1 = 0
    pass

  return roc_train, roc_valid, f1_score, recall_1, precision_1

In [1544]:
# так как Random Forest склонен к переобучению 
# попробуем направить optimize в сторону уменьшения roc_train
# cоздаем объект исследования
optuna_study_rf = optuna.create_study(study_name='RandomForestClassifier_'+feature_space+'_torow', 
                               directions=['minimize','maximize','maximize','maximize','maximize'], 
                               sampler=optuna.samplers.TPESampler(),
                               pruner='Hyperband',
                               storage='sqlite:///optuna_studies.db',
                               load_if_exists=True)
# на случай удаления 
# optuna.delete_study(study_name='RandomForestClassifier_'+feature_space+'_torow', storage='sqlite:///optuna_studies.db')

[I 2025-04-19 14:06:21,493] Using an existing study with name 'RandomForestClassifier_credit_torow' instead of creating a new one.


In [258]:
# ищем лучшую комбинацию гиперпараметров n_trials раз
optuna_study_rf.optimize(optuna_rf, n_trials=300)

[I 2025-04-17 12:41:48,217] Trial 0 finished with values: [0.6930647049075256, 0.637121546628082, 0.06789637867896378, 1.0, 0.035141168377160345] and parameters: {'n_estimators': 120, 'criterion': 'log_loss', 'max_depth': 13, 'min_samples_split': 10, 'min_samples_leaf': 16, 'max_features': 0.36140005508656686, 'max_samples': 0.37588857468425946, 'class_0_weight': 0.2479038533619358, 'class_1_weight': 0.5756309144041182, 'n_last': 7, 'class_1_percent': 0.5885455847977769, 'random_state': 703345}.
[I 2025-04-17 12:41:52,181] Trial 1 finished with values: [0.6536306805091827, 0.622748130407649, 0.06787520507640367, 1.0, 0.03512982456140351] and parameters: {'n_estimators': 120, 'criterion': 'log_loss', 'max_depth': 12, 'min_samples_split': 14, 'min_samples_leaf': 25, 'max_features': 0.7345449408458101, 'max_samples': 0.6402936212108844, 'class_0_weight': 0.8218390842187012, 'class_1_weight': 0.8196576393520376, 'n_last': 15, 'class_1_percent': 0.9040554132305438, 'random_state': 189759}.


In [1545]:
# из полученного результат соврмируем Data Frame
optuna_study_rf_pd = optuna_study_rf.trials_dataframe().dropna()
# переименуем столбы
optuna_study_rf_pd.rename(columns={
    'values_0': 'roc_train',
    'values_1': 'roc_valid',
    'values_2': 'f1_score',
    'values_3': 'recall_1',
    'values_4': 'precision_1'
},inplace=True)
optuna_study_rf_pd.sort_values(by='precision_1').drop(['datetime_start','datetime_complete','duration'],axis=1)

number  roc_train  roc_valid  f1_score  recall_1  precision_1  \
70       70   0.902309   0.647039  0.000000  0.000000     0.000000   
169     169   0.705537   0.643032  0.000000  0.000000     0.000000   
95       95   0.723563   0.651726  0.000000  0.000000     0.000000   
24       24   0.820705   0.638212  0.000000  0.000000     0.000000   
220     220   0.671428   0.633940  0.000000  0.000000     0.000000   
..      ...        ...        ...       ...       ...          ...   
187     187   0.705436   0.644999  0.004747  0.002397     0.240000   
170     170   0.727078   0.645240  0.002386  0.001199     0.250000   
41       41   0.756688   0.649510  0.001594  0.000799     0.333333   
297     297   0.685123   0.639782  0.001594  0.000799     0.333333   
152     152   0.719954   0.646584  0.001596  0.000799     0.500000   

     params_class_0_weight  params_class_1_percent  params_class_1_weight  \
70                0.679543                0.013678               0.839585   
169               0.998973                0.271907               0.355675   
95                0.651261                0.199795               0.382488   
24                0.401538                0.036104               0.173766   
220               0.933268                0.302441               0.546183   
..                     ...                     ...                    ...   
187               0.868235                0.240363               0.466833   
170               0.961709                0.298328               0.308424   
41                0.365391                0.186405               0.300503   
297               0.877455                0.504246               0.054558   
152               0.817644                0.455040               0.122343   

    params_criterion  params_max_depth  params_max_features  \
70           entropy                18             0.687022   
169          entropy                11             0.486260   
95              gini                19             0.752988   
24          log_loss                14             0.300616   
220             gini                 9             0.170454   
..               ...               ...                  ...   
187          entropy                11             0.635603   
170          entropy                12             0.473325   
41              gini                16             0.389122   
297          entropy                11             0.873693   
152          entropy                13             0.549999   

     params_max_samples  params_min_samples_leaf  params_min_samples_split  \
70             0.341553                       22                        15   
169            0.558218                       16                         7   
95             0.174406                       23                        13   
24             0.241607                        9                         9   
220            0.323146                        5                        13   
..                  ...                      ...                       ...   
187            0.239367                       15                        12   
170            0.995583                       16                         8   
41             0.408510                       23                        10   
297            0.404193                       13                        12   
152            0.878299                       20                        14   

     params_n_estimators  params_n_last  params_random_state     state  
70                   110             14               632290  COMPLETE  
169                  110              5               302767  COMPLETE  
95                   115             15               275306  COMPLETE  
24                   130             23               624642  COMPLETE  
220                   95              5               480906  COMPLETE  
..                   ...            ...                  ...       ...  
187                  115          

In [1547]:
# покаждем статистику обучения
print('Максимальное значение метрики ROC AUC на валидационном наборе:',round(optuna_study_rf_pd['roc_valid'].max(),3))
print('Среднее значение метрики ROC AUC на валидационном наборе:',round(optuna_study_rf_pd['roc_valid'].mean(),3))
print('Максимальное значение метрики f1_score на валидационном наборе:',round(optuna_study_rf_pd['f1_score'].max(),3))
print('Среднее значение метрики f1_score на валидационном наборе:',round(optuna_study_rf_pd['f1_score'].mean(),3))
print('Максимальное значение метрики recall_1 на валидационном наборе:',round(optuna_study_rf_pd['recall_1'].max(),3))
print('Среднее значение метрики recall_1 на валидационном наборе:',round(optuna_study_rf_pd['recall_1'].mean(),3))
print('Максимальное значение метрики precision_1 на валидационном наборе:',round(optuna_study_rf_pd['precision_1'].max(),3))
print('Среднее значение метрики precision_1 на валидационном наборе:',round(optuna_study_rf_pd['precision_1'].mean(),3))

Максимальное значение метрики ROC AUC на валидационном наборе: 0.653
Среднее значение метрики ROC AUC на валидационном наборе: 0.636
Максимальное значение метрики f1_score на валидационном наборе: 0.119
Среднее значение метрики f1_score на валидационном наборе: 0.078
Максимальное значение метрики recall_1 на валидационном наборе: 1.0
Среднее значение метрики recall_1 на валидационном наборе: 0.487
Максимальное значение метрики precision_1 на валидационном наборе: 0.5
Среднее значение метрики precision_1 на валидационном наборе: 0.064


In [1549]:
# Построим зависимость метрик качества модели от number

fig = px.scatter(
    data_frame=optuna_study_rf_pd[(optuna_study_rf_pd['roc_valid']>=0.6)&
                                  (optuna_study_rf_pd['f1_score']>=0.99*(optuna_study_rf_pd['f1_score'].max()))
                                   ],
    x='number', #ось абсцисс
    y=['roc_valid','roc_train','precision_1','recall_1','f1_score'], #ось ординат
)
fig.update_layout(
    title ={
        'text':'Зависимость метрик качества модели от number', # Имя рабочей плоскости
        'font':{'size':35,'family':"Times New Roman"}, # размер и стиль написания имени рабочей плоскости
        'x':0.5, # Смешение имени по оси "x" на половину рабочей плоскости
        },
    height =800,# Высота рабочей плоскости
    width = 1350, # Ширина рабочей плоскости
    bargap=0.2, # Добавил расстояния между столбами гистограммы
    xaxis_title='Величина метрики ROC Valid',
    yaxis_title='Величина параметра')
fig.update_xaxes(showspikes=True)
fig.update_yaxes(showspikes=True)

fig.show()

<span style="color:Blue">

Вывод:  

Их всех выбираем точку $number =168$.   
В этой точке оптимальные значения метрик $recall_1$ и $precision_1$, а  
также относительно высокая метрика $ROC AUC$.   
Посмотрим каким значениям гиперпараметров соотвествует выбраннаяточка.

In [1550]:
# определим номер лучшге варианта
best_optuna_number = 168

# сформируем словарь лучших гипирпарметров RandomForestClassifier
best_param_rf = {
    'n_estimators' : int(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_n_estimators'].iloc[0]),
    'criterion': optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_criterion'].iloc[0],
    'max_depth' : optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_max_depth'].iloc[0],
    'min_samples_split': optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_min_samples_split'].iloc[0],
    'min_samples_leaf' : optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_min_samples_leaf'].iloc[0],
    'max_features': optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_max_features'].iloc[0],
    'max_samples' : optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_max_samples'].iloc[0],
    'class_weight' : {0:optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_class_0_weight'].iloc[0],
                      1:optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_class_1_weight'].iloc[0]}
    }
# определим перменные для лучших значений параметров
best_n_last = optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_n_last'].iloc[0]
best_class_1_percent = optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_class_1_percent'].iloc[0]
best_random_state = optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_random_state'].iloc[0]


# Выведем принятые наилучшие праметры
print('best n estimators:',best_param_rf['n_estimators'])
print('best criterion:',best_param_rf['criterion'])
print('best max depth:',best_param_rf['max_depth'])
print('best min samples split:',best_param_rf['min_samples_split'])
print('best min samples leaf:',best_param_rf['min_samples_leaf'])
print('best max features(%):',round(best_param_rf['max_features'],3))
print('best max samples(%):',round(best_param_rf['max_samples'],3))
print('best class 0 weight:',round(best_param_rf['class_weight'][0],3))
print('best class 1 weight:',round(best_param_rf['class_weight'][1],3))

print('best class 1 percent:',round(best_class_1_percent,3))
print('best n last:',best_n_last)
print('best random state:',best_random_state)
print('time for best train:',round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['duration'].iloc[0].seconds/60),'minutes')

print()
print('ROC AUC на обучающем наборе:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['roc_train'].iloc[0],3))
print('ROC AUC на валидационном наборе:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['roc_valid'].iloc[0],3))
print('precision класса 1:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['precision_1'].iloc[0],3))
print('recall класса 1:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['recall_1'].iloc[0],3))

best n estimators: 115
best criterion: entropy
best max depth: 11
best min samples split: 15
best min samples leaf: 23
best max features(%): 0.832
best max samples(%): 0.31
best class 0 weight: 0.926
best class 1 weight: 0.687
best class 1 percent: 0.48
best n last: 5
best random state: 434941
time for best train: 0 minutes

ROC AUC на обучающем наборе: 0.681
ROC AUC на валидационном наборе: 0.645
precision класса 1: 0.079
recall класса 1: 0.23


##### <span style="color:MediumSlateBlue">Обучение модели с лучшими параметрами</span>

In [1551]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'credit'
count_features = dict_spaces[feature_space]

# с помощью функции features_from_transform_data_torow извлечем  
# из данных transform_data_torow
# признаки сооствествующие n_last последним клиенским операциям
list_n_last_features = features_from_transform_data_torow(best_n_last,count_features,25)

# загружаем обучующие наборы
X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)

# подготовим данные для обучения модели
# с помощью функции class_1_percent_samples зададим долю 
# класса 1
list_c1_percent_id = class_1_percent_samples(y_train_pd,best_class_1_percent,random_state=best_random_state)[:1000000]

# сформируем данные для обучения базовой модели
X_train_balanced = np.array(X_train_pd.loc[list_c1_percent_id])[:,list_n_last_features]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

# освободим память от "тяжелых" и ненужных файлов
del X_train_pd, y_train_pd
gc.collect()

# обучаем модель RandomForestClassifier с наилучшеми параметрами
random_forest = RandomForestClassifier(
        **best_param_rf,
        n_jobs=-1,
        random_state=best_random_state)
random_forest.fit(X_train_balanced, y_train_balanced)

# освободим память от "тяжелых" и ненужных файлов
del X_train_balanced, y_train_balanced
gc.collect()


# подгружаем данные для тестирования
X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()[:,list_n_last_features]
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()[:,list_n_last_features]
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_rf__pred_proba = random_forest.predict_proba(X_train)[:,1]
y_valid_rf_pred_proba = random_forest.predict_proba(X_valid)[:,1]

# Делаем предсказание для валидационной выборки
y_valid_rf_pred = random_forest.predict(X_valid)

# удаляем крупные файлы чтобы высвободить память 
del X_train, X_valid
gc.collect()

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_rf__pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_rf_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_rf_pred,zero_division=0))

# time: 2m 10s

ROC AUC на обучающем наборе 0.681
ROC AUC на валидационном наборе 0.645
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.97      0.90      0.93     68747
           1       0.08      0.23      0.12      2503

    accuracy                           0.88     71250
   macro avg       0.52      0.57      0.53     71250
weighted avg       0.94      0.88      0.91     71250



#### <span style="color:MediumBlue">Построение модели Gradient Boosting Classifier</span>

##### <span style="color:MediumSlateBlue">Формирование данных для обучения</span>

Анализ исходных данных, в частности target, показал что представленные данные   
имееют перекос: 96% клиентов у которых не случился дефолт (flag = 0),    
против 4 % - для которых произошел дефолт (flag = 1).  
С помощью функции class_1_percent_samples, сформируем сбаланисрованную выборку  
для обучения моделей.
За основу сбалансировных данных возьмем данные клиентов с дефолтом  
и к ним будем добирать необходимое количество клиентов до сбалансированности. 


Функция class_1_percent_samples принемает две переменные:
- target_data - массив с id и целевой переменной
- class_1_percent - процент класса 1 в результирующем массиве

In [1395]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'credit'
count_features = dict_spaces[feature_space]

In [1396]:
# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

In [1397]:
# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)
y_train_pd.head(4)

id  flag
id                    
1825800  1825800     0
2166483  2166483     0
2534345  2534345     0
1803283  1803283     0

In [1398]:
# взглянем на сблансиорованность данных в y_train
y_train_pd['flag'].value_counts(normalize=True)

flag
0    0.964242
1    0.035758
Name: proportion, dtype: float64

In [1399]:
# сбалансируем данные в y_train_pd
list_c1_percent_id = class_1_percent_samples(y_train_pd,0.5)
# list_c1_percent_features - список 'id' из y_train_pd соотвествующих  
# заданному проценту класса 1
len(list_c1_percent_id)

45860

In [1400]:
# проверим сбалансированность полученного y_train
y_train_pd.loc[list_c1_percent_id]['flag'].value_counts(normalize=True)

flag
1    0.5
0    0.5
Name: proportion, dtype: float64

*transform_data_torow*, показываеются последние N операций клиента.  
В данных в *date_torow*, собраны последние 25 операций клиентов.

Предварительный анализ показывает, что медиальное значение количества клиентских  
операций равно 7. Поэтому, для начала, будем показывать моделе $n_{last} = 7$   
последних клиентских операций.

Для извлечения из *transform_data_torow_25* необходимого количества последних клиенских  
операций ($n_{last}$) используем функцию features_from_transform_data_torow.

Функция features_from_transform_data_torow примает следующие аргументы:
- $n_{last} = 7$ - необходимое количество последних клиентских операций; 
- $n_{groups} = 8$ - количество признаков в $date$ $features$;
- $N_{last} = 25$ - количество $n_{last}$ операций, показанных в transform_data_torow_25


In [1401]:
# с помощью функции features_from_transform_data_torow извлечем  
# из данных transform_data_torow_25
# признаки сооствествующие 7 последним клиенским операциям
list_n_last_features = features_from_transform_data_torow(7,count_features,25)

In [1402]:
# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']
# сформируем данные для проверики модели
X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

In [1403]:
# посмотрим на структуру данных в X_train_balanced
X_train_balanced.head(2)

f1  f2  f3  f4  f5  f6  f7  f8  f9  f10  ...  f91  f92  f93  f94  \
id                                                ...                       
2335465   0  16  11  19  16   0   6  19  19    6  ...    7    2    0    0   
390270   10   5  19  12  13   2   0   0   0    0  ...    0    0    0    0   

         f95  f96  f97  f98  f99  f100  
id                                      
2335465    0    0    0    0    0     0  
390270     0    0    0    0    0     0  

[2 rows x 100 columns]

In [1404]:
# посмотрим на структуру данных в y_train_balanced
y_train_balanced.head(2)

id
2335465    1
390270     1
Name: flag, dtype: int64

In [1405]:
# проверим что выборки действительно совпадают по id
X_train_balanced.index.to_list() == y_train_balanced.index.to_list()

True

##### <span style="color:MediumSlateBlue">Baseline обучение модели Hist Gradient Boosting Classifier</span>

In [1406]:
# обучаем модель Gradient Boosting Classifier
gradient_boosting = HistGradientBoostingClassifier(random_state=42)
gradient_boosting.fit(np.array(X_train_balanced)[:,list_n_last_features],np.array(y_train_balanced))

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_rf__pred_proba = gradient_boosting.predict_proba(X_train[:,list_n_last_features])[:,1]
y_valid_rf_pred_proba = gradient_boosting.predict_proba(X_valid[:,list_n_last_features])[:,1]

# Делаем предсказание для валидационной выборки
y_valid_rf_pred = gradient_boosting.predict(X_valid[:,list_n_last_features])

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_rf__pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_rf_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_rf_pred))

# time: 

ROC AUC на обучающем наборе 0.698
ROC AUC на валидационном наборе 0.662
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.98      0.62      0.76     68747
           1       0.05      0.61      0.10      2503

    accuracy                           0.62     71250
   macro avg       0.52      0.61      0.43     71250
weighted avg       0.95      0.62      0.73     71250



##### <span style="color:MediumSlateBlue">Подбор гиперпараметров модели</span>

In [1552]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'credit'
count_features = dict_spaces[feature_space]

# настроим оптимизацию гипер параметров
def optuna_hgbc(trial):
  # задаем пространства поиска гиперпараметров
  learning_rate = trial.suggest_float('learning_rate',0.2,0.6)
  max_iter = trial.suggest_int('max_iter', 50, 300,step = 1)
  max_leaf_nodes = trial.suggest_int('max_leaf_nodes', 2, 50,step = 1)
  max_depth = trial.suggest_int('max_depth', 1, 15,step = 1)
  min_samples_leaf = trial.suggest_int('min_samples_leaf', 1, 50,step = 1)
  max_features = trial.suggest_float('max_features',0.1,1)
  l2_regularization = trial.suggest_float('l2_regularization',0.01,1)
  class_0_weight = trial.suggest_float('class_0_weight',0.01,1)
  class_1_weight = trial.suggest_float('class_1_weight',0.01,1)
  n_last = trial.suggest_int('n_last', 5, 25,step = 1)
  class_1_percent = trial.suggest_float('class_1_percent',0.01,1)
  random_state = trial.suggest_int('random_state', 1, 1000000)


  # создаем модель
  optuna_gradient_boosting = HistGradientBoostingClassifier(
      learning_rate= learning_rate,
      max_iter = max_iter,
      max_leaf_nodes =max_leaf_nodes,
      max_depth = max_depth,
      min_samples_leaf = min_samples_leaf,
      max_features=max_features,
      l2_regularization = l2_regularization,
      class_weight={0:class_0_weight,1:class_1_weight},
      random_state=42)

  # с помощью функции features_from_transform_data_torow извлечем  
  # из данных transform_data_torow
  # признаки сооствествующие n_last последним клиенским операциям
  list_n_last_features = features_from_transform_data_torow(n_last,count_features,25)

  # загружаем обучующие наборы
  X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
  y_train_pd = pd.read_csv('target/target_train.csv')

  # поготовим данные y_train_pd к работе с функцией class_1_percent_samples
  y_train_pd.set_index('id',drop=False,inplace=True)

  # подготовим данные для обучения модели
  # с помощью функции class_1_percent_samples зададим долю класса 1
  list_c1_percent_id = class_1_percent_samples(y_train_pd,class_1_percent,random_state=random_state)[:1000000]

  # сформируем данные для обучения модели
  X_train_balanced = np.array(X_train_pd.loc[list_c1_percent_id])[:,list_n_last_features]
  y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

  # освободим память от "тяжелых" и ненужных файлов
  del X_train_pd, y_train_pd
  gc.collect()

  # я не воспользовался параметром timeout метода optimize потому, что  
  # optimize отставливает поиск параметров, если время обучения 
  # превышает timeout. Мне нужно чтобы поиск параметров продолжился.
  try:
    # для модуля func_time_out упакуем обучение модели в функцию try_func
    def try_func():
            return optuna_gradient_boosting.fit(X_train_balanced,y_train_balanced)
    # обучаем модель с ограничением по времени 10 минут (600 секунд)
    optuna_gradient_boosting = func_timeout.func_timeout(600, try_func)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train_balanced, y_train_balanced
    gc.collect()

    # подгружаем данные для тестирования
    X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()[:,list_n_last_features]
    y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
    X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()[:,list_n_last_features]
    y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

    # делаем предсказание на обучающем и валидационном наборе и считаем метрики
    roc_train = metrics.roc_auc_score(y_train, optuna_gradient_boosting.predict_proba(X_train)[:,1])
    roc_valid = metrics.roc_auc_score(y_valid, optuna_gradient_boosting.predict_proba(X_valid)[:,1])
    f1_score = metrics.f1_score(y_valid, optuna_gradient_boosting.predict(X_valid))
    recall_1 = metrics.recall_score(y_valid, optuna_gradient_boosting.predict(X_valid),average=None,zero_division=0)[1]
    precision_1 = metrics.precision_score(y_valid, optuna_gradient_boosting.predict(X_valid),average=None,zero_division=0)[1]

    # удаляем крупные файлы чтобы высвободить память 
    del X_train, X_valid, y_train, y_valid 
    gc.collect()

  except func_timeout.FunctionTimedOut:
    # освободим память от "тяжелых" и ненужных файлов
    del X_train_balanced, y_train_balanced
    gc.collect()

    # обьявим метрики пустыми значениями
    roc_train = 0
    roc_valid = 0
    f1_score = 0
    recall_1 = 0
    precision_1 = 0
    pass

  return roc_train, roc_valid, f1_score, recall_1, precision_1

In [1553]:
# cоздаем объект исследования
# чтобы модель не переобучалась минимизируем roc_train 
# и максимизируем roc_valid
optuna_study_hsbs = optuna.create_study(study_name='HistGradientBoostingClassifier_'+feature_space+'_torow', 
                               directions=['maximize','maximize','maximize','maximize','maximize'], 
                               sampler=optuna.samplers.TPESampler(),
                               pruner='Hyperband',
                               storage='sqlite:///optuna_studies.db',
                               load_if_exists=True)

# ну случай удаления обучения
# optuna.delete_study(study_name='HistGradientBoostingClassifier_'+feature_space+'_torow', storage='sqlite:///optuna_studies.db')

[I 2025-04-19 14:07:32,620] Using an existing study with name 'HistGradientBoostingClassifier_credit_torow' instead of creating a new one.


In [290]:
# ищем лучшую комбинацию гиперпараметров n_trials раз
optuna_study_hsbs.optimize(optuna_hgbc, n_trials=300)

[I 2025-04-17 13:12:05,164] Trial 0 finished with values: [0.675547415821733, 0.661850488274094, 0.0007987220447284345, 0.00039952057530962844, 1.0] and parameters: {'learning_rate': 0.3667058335235604, 'max_iter': 71, 'max_leaf_nodes': 7, 'max_depth': 9, 'min_samples_leaf': 5, 'max_features': 0.5777127197033602, 'l2_regularization': 0.919663430497384, 'class_0_weight': 0.8707593461051678, 'class_1_weight': 0.995124873550114, 'n_last': 5, 'class_1_percent': 0.0903986443918365, 'random_state': 982517}.
[I 2025-04-17 13:12:07,572] Trial 1 finished with values: [0.5905572701548761, 0.5722325116416224, 0.06804407338299988, 0.9980023971234518, 0.03522278623801466] and parameters: {'learning_rate': 0.5023706692751694, 'max_iter': 243, 'max_leaf_nodes': 44, 'max_depth': 14, 'min_samples_leaf': 36, 'max_features': 0.2609997562275314, 'l2_regularization': 0.06672375405000136, 'class_0_weight': 0.4504856261488571, 'class_1_weight': 0.6772165109555992, 'n_last': 20, 'class_1_percent': 0.921607450

In [1554]:
# из полученного результат соврмируем Data Frame
optuna_study_hsbs_pd = optuna_study_hsbs.trials_dataframe()
# переименуем столбы
optuna_study_hsbs_pd.rename(columns={
    'values_0': 'roc_train',
    'values_1': 'roc_valid',
    'values_2': 'f1_score',
    'values_3': 'recall_1',
    'values_4': 'precision_1'
},inplace=True)
# Выделим время потраченное на обучение модели
last_trail = optuna_study_hsbs_pd['number'].max()
optuna_study_hsbs_pd.tail(5)


number  roc_train  roc_valid  f1_score  recall_1  precision_1  \
295     295   0.721811   0.667433  0.108770  0.556932     0.060271   
296     296   0.721237   0.669610  0.061586  0.039553     0.139045   
297     297   0.728867   0.664621  0.044578  0.026768     0.133201   
298     298   0.722804   0.662784  0.102280  0.605673     0.055856   
299     299   0.732566   0.666971  0.055655  0.037155     0.110846   

                datetime_start          datetime_complete  \
295 2025-04-17 13:37:48.782331 2025-04-17 13:37:58.144915   
296 2025-04-17 13:37:58.151317 2025-04-17 13:38:07.867112   
297 2025-04-17 13:38:07.872565 2025-04-17 13:38:18.583637   
298 2025-04-17 13:38:18.589378 2025-04-17 13:38:27.687116   
299 2025-04-17 13:38:27.693451 2025-04-17 13:38:39.209384   

                  duration  params_class_0_weight  ...  \
295 0 days 00:00:09.362584               0.049617  ...   
296 0 days 00:00:09.715795               0.101025  ...   
297 0 days 00:00:10.711072               0.099453  ...   
298 0 days 00:00:09.097738               0.065324  ...   
299 0 days 00:00:11.515933               0.078347  ...   

     params_l2_regularization  params_learning_rate  params_max_depth  \
295                  0.071318              0.237096                15   
296                  0.056934              0.256529                15   
297                  0.094816              0.253867                15   
298                  0.056164              0.260782                14   
299                  0.013150              0.246246                15   

     params_max_features  params_max_iter  params_max_leaf_nodes  \
295             0.968841              287                     45   
296             0.960249              176                     46   
297             0.927278              158                     46   
298             0.965214              274                     47   
299             0.981733              281                     48   

     params_min_samples_leaf  params_n_last  params_random_state     state  
295                       26             15               291070  COMPLETE  
296                       25             16               276785  COMPLETE  
297                       28             16               236639  COMPLETE  
298                       23             16               268652  COMPLETE  
299                       26             16               319997  COMPLETE  

[5 rows x 22 columns]

In [1555]:
# покаждем статистику обучения
print('Максимальное значение метрики ROC AUC на валидационном наборе:',round(optuna_study_hsbs_pd['roc_valid'].max(),3))
print('Среднее значение метрики ROC AUC на валидационном наборе:',round(optuna_study_hsbs_pd['roc_valid'].mean(),3))
print('Максимальное значение метрики f1_score на валидационном наборе:',round(optuna_study_hsbs_pd['f1_score'].max(),3))
print('Среднее значение метрики f1_score на валидационном наборе:',round(optuna_study_hsbs_pd['f1_score'].mean(),3))
print('Максимальное значение метрики recall_1 на валидационном наборе:',round(optuna_study_hsbs_pd['recall_1'].max(),3))
print('Среднее значение метрики recall_1 на валидационном наборе:',round(optuna_study_hsbs_pd['recall_1'].mean(),3))
print('Максимальное значение метрики precision_1 на валидационном наборе:',round(optuna_study_hsbs_pd['precision_1'].max(),3))
print('Среднее значение метрики precision_1 на валидационном наборе:',round(optuna_study_hsbs_pd['precision_1'].mean(),3))

Максимальное значение метрики ROC AUC на валидационном наборе: 0.671
Среднее значение метрики ROC AUC на валидационном наборе: 0.658
Максимальное значение метрики f1_score на валидационном наборе: 0.13
Среднее значение метрики f1_score на валидационном наборе: 0.087
Максимальное значение метрики recall_1 на валидационном наборе: 1.0
Среднее значение метрики recall_1 на валидационном наборе: 0.417
Максимальное значение метрики precision_1 на валидационном наборе: 1.0
Среднее значение метрики precision_1 на валидационном наборе: 0.078


In [1559]:
# Построим зависимость метрик качества модели от number

fig = px.scatter(
    data_frame=optuna_study_hsbs_pd[(optuna_study_hsbs_pd['roc_valid']>0.67)&
                                    (optuna_study_hsbs_pd['f1_score']>0.9*optuna_study_hsbs_pd['f1_score'].max())],
    x='number', #ось абсцисс
    y=['roc_train','roc_valid','recall_1','precision_1','f1_score'], #ось ординат
)
fig.update_layout(
    title ={
        'text':'Зависимость precision от гиперпараметров модели', # Имя рабочей плоскости
        'font':{'size':35,'family':"Times New Roman"}, # размер и стиль написания имени рабочей плоскости
        'x':0.5, # Смешение имени по оси "x" на половину рабочей плоскости
        },
    height =800,# Высота рабочей плоскости
    width = 1350, # Ширина рабочей плоскости
    bargap=0.2, # Добавил расстояния между столбами гистограммы
    xaxis_title='Величина метрики precision_1',
    yaxis_title='Величина параметра')
fig.update_xaxes(showspikes=True)
fig.update_yaxes(showspikes=True)

fig.show()

<span style="color:Blue">

Вывод:  

Их всех выбираем точку $number =264$.   
В этой точке оптимальные значения метрик $recall_1$ и $precision_1$, а  
также относительно высокая метрика $ROC AUC$.   
Посмотрим каким значениям гиперпараметров соотвествует выбранная точка.

In [1560]:
# определим номер лучшге варианта
best_optuna_number = 264

# сформируем словарь лучших гипирпарметров RandomForestClassifier
best_param_rf = {
    'learning_rate' : optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_learning_rate'].iloc[0],
    'max_iter' : optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_max_iter'].iloc[0],
    'max_leaf_nodes' : optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_max_leaf_nodes'].iloc[0],
    'max_depth' : optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_max_depth'].iloc[0],
    'min_samples_leaf' : optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_min_samples_leaf'].iloc[0],
    'max_features' : optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_max_features'].iloc[0],
    'l2_regularization' : optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_l2_regularization'].iloc[0],
    'class_weight' : {0: optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_class_0_weight'].iloc[0],
                      1: optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_class_1_weight'].iloc[0],}
    }

# определим перменные для лучших значений параметров
best_n_last = optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_n_last'].iloc[0]
best_class_1_percent = optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_class_1_percent'].iloc[0]
best_random_state = optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_random_state'].iloc[0]


# Выведем принятые наилучшие праметры
print('best learning rate:',round(best_param_rf['learning_rate'],3))
print('best max iter:',best_param_rf['max_iter'])
print('best max leaf nodes:',best_param_rf['max_leaf_nodes'])
print('best max depth:',best_param_rf['max_depth'])
print('best min samples leaf:',best_param_rf['min_samples_leaf'])
print('best max features:',round(best_param_rf['max_features'],3))
print('best l2 regularization:',round(best_param_rf['l2_regularization'],3))
print('best class 0 weight:',round(best_param_rf['class_weight'][0],3))
print('best class 1 weight:',round(best_param_rf['class_weight'][1],3))

print('best class 1 percent:',round(best_class_1_percent,3))
print('best n last:',best_n_last)
print('best random state:',best_random_state)
print('time for best train:',round(optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['duration'].iloc[0].seconds/60),'minutes')

print()
print('ROC AUC на обучающем наборе:', round(optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['roc_train'].iloc[0],3))
print('ROC AUC на валидационном наборе:', round(optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['roc_valid'].iloc[0],3))
print('precision класса 1:', round(optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['precision_1'].iloc[0],3))
print('recall класса 1:', round(optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['recall_1'].iloc[0],3))

best learning rate: 0.254
best max iter: 291
best max leaf nodes: 47
best max depth: 15
best min samples leaf: 24
best max features: 0.969
best l2 regularization: 0.012
best class 0 weight: 0.033
best class 1 weight: 0.706
best class 1 percent: 0.035
best n last: 16
best random state: 536960
time for best train: 0 minutes

ROC AUC на обучающем наборе: 0.733
ROC AUC на валидационном наборе: 0.671
precision класса 1: 0.069
recall класса 1: 0.408


##### <span style="color:MediumSlateBlue">Обучение модели с лучшими параметрами</span>

In [1561]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'credit'
count_features = dict_spaces[feature_space]

# с помощью функции features_from_transform_data_torow извлечем  
# из данных transform_data_torow
# признаки сооствествующие n_last последним клиенским операциям
list_n_last_features = features_from_transform_data_torow(best_n_last,count_features,25)

# загружаем обучующие наборы
X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)

# подготовим данные для обучения модели
# с помощью функции class_1_percent_samples зададим долю класса 1
list_c1_percent_id = class_1_percent_samples(y_train_pd,best_class_1_percent,random_state=best_random_state)[:1000000]

# сформируем данные для обучения модели
X_train_balanced = np.array(X_train_pd.loc[list_c1_percent_id])[:,list_n_last_features]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

# освободим память от "тяжелых" и ненужных файлов
del X_train_pd, y_train_pd
gc.collect()


# обучаем модель HistGradientBoostingClassifier с наилучшеми параметрами
gradient_boosting = HistGradientBoostingClassifier(
        **best_param_rf,
        random_state=42)
gradient_boosting.fit(X_train_balanced,y_train_balanced)

# освободим память от "тяжелых" и ненужных файлов
del X_train_balanced, y_train_balanced
gc.collect()

# подгружаем данные для тестирования
X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()[:,list_n_last_features]
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()[:,list_n_last_features]
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_gb__pred_proba = gradient_boosting.predict_proba(X_train)[:,1]
y_valid_gb_pred_proba = gradient_boosting.predict_proba(X_valid)[:,1]

# Делаем предсказание для валидационной выборки
y_valid_gb_pred = gradient_boosting.predict(X_valid)

# освободим память от "тяжелых" и ненужных файлов
del X_train, X_valid
gc.collect()

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_gb__pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_gb_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_gb_pred,zero_division=0))

# time: 2m 30s

ROC AUC на обучающем наборе 0.729
ROC AUC на валидационном наборе 0.669
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.97      0.80      0.88     68747
           1       0.07      0.42      0.12      2503

    accuracy                           0.78     71250
   macro avg       0.52      0.61      0.50     71250
weighted avg       0.94      0.78      0.85     71250



### <span style="color:RoyalBlue">Построение модели на сбалансированных данных подпространства relative torow</span>

#### <span style="color:MediumBlue">Построение модели Logistic Regression</span>

##### <span style="color:MediumSlateBlue">Формирование данных для обучения</span>

Анализ исходных данных, в частности target, показал что представленные данные   
имееют перекос: 96% клиентов у которых не случился дефолт (flag = 0),    
против 4 % - для которых произошел дефолт (flag = 1).  
С помощью функции class_1_percent_samples, сформируем сбаланисрованную выборку  
для обучения моделей.
За основу сбалансировных данных возьмем данные клиентов с дефолтом  
и к ним будем добирать необходимое количество клиентов до сбалансированности. 


Функция class_1_percent_samples принемает две переменные:
- target_data - массив с id и целевой переменной
- class_1_percent - процент класса 1 в результирующем массиве

In [309]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'relative'
count_features = dict_spaces[feature_space]

In [310]:
# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

In [311]:
# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)
y_train_pd.head(4)

id  flag
id                    
1825800  1825800     0
2166483  2166483     0
2534345  2534345     0
1803283  1803283     0

In [312]:
# взглянем на сблансиорованность данных в y_train
y_train_pd['flag'].value_counts(normalize=True)

flag
0    0.964242
1    0.035758
Name: proportion, dtype: float64

In [313]:
# сбалансируем данные в y_train_pd
list_c1_percent_id = class_1_percent_samples(y_train_pd,0.5)
# list_c1_percent_features - список 'id' из y_train_pd соотвествующих  
# заданному проценту класса 1
len(list_c1_percent_id)

45860

In [314]:
# проверим сбалансированность полученного y_train
y_train_pd.loc[list_c1_percent_id]['flag'].value_counts(normalize=True)

flag
1    0.5
0    0.5
Name: proportion, dtype: float64

*transform_data_torow*, показываеются последние N операций клиента.  
В данных в *date_torow*, собраны последние 25 операций клиентов.

Предварительный анализ показывает, что медиальное значение количества клиентских  
операций равно 7. Поэтому, для начала, будем показывать моделе $n_{last} = 7$   
последних клиентских операций.

Для извлечения из *transform_data_torow_25* необходимого количества последних клиенских  
операций ($n_{last}$) используем функцию features_from_transform_data_torow.

Функция features_from_transform_data_torow примает следующие аргументы:
- $n_{last} = 7$ - необходимое количество последних клиентских операций; 
- $n_{groups} = 8$ - количество признаков в $date$ $features$;
- $N_{last} = 25$ - количество $n_{last}$ операций, показанных в transform_data_torow_25


In [315]:
# с помощью функции features_from_transform_data_torow извлечем  
# из данных transform_data_torow_25
# признаки сооствествующие 7 последним клиенским операциям
list_n_last_features = features_from_transform_data_torow(7,count_features,25)

In [316]:
# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']
# сформируем данные для проверики модели
X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

In [317]:
# посмотрим на структуру данных в X_train_balanced
X_train_balanced.head(2)

f1  f2  f3  f4  f5  f6  f7  f8  f9  f10  ...  f141  f142  f143  f144  \
id                                                ...                           
2335465   6  11  16  16  16  16  16  16  16   16  ...     1     1     0     0   
390270   15  11   0  16  16  16   0   0   0    0  ...     0     0     0     0   

         f145  f146  f147  f148  f149  f150  
id                                           
2335465     0     0     0     0     0     0  
390270      0     0     0     0     0     0  

[2 rows x 150 columns]

In [318]:
# посмотрим на структуру данных в y_train_balanced
y_train_balanced.head(2)

id
2335465    1
390270     1
Name: flag, dtype: int64

In [319]:
# проверим что выборки действительно совпадают по id
X_train_balanced.index.to_list() == y_train_balanced.index.to_list()

True

##### <span style="color:MediumSlateBlue">Baseline обучение модели LogisticRegression</span>

In [320]:
# обучаем модель логистической регрессии
logistic_regression = linear_model.LogisticRegression(random_state=42, max_iter=10000)
logistic_regression.fit(np.array(X_train_balanced)[:,list_n_last_features],np.array(y_train_balanced))

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_LR_pred_proba = logistic_regression.predict_proba(X_train[:,list_n_last_features])[:,1]
y_valid_LR_pred_proba = logistic_regression.predict_proba(X_valid[:,list_n_last_features])[:,1]

# Делаем предсказание для валидационной выборки
y_valid_LR_pred = logistic_regression.predict(X_valid[:,list_n_last_features])

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_LR_pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_LR_pred_proba),3))

print('Основные метрики на тестовом наборе:')
print(metrics.classification_report(y_valid,y_valid_LR_pred))

# time: 1m 12s

ROC AUC на обучающем наборе 0.603
ROC AUC на валидационном наборе 0.61
Основные метрики на тестовом наборе:
              precision    recall  f1-score   support

           0       0.97      0.59      0.74     68747
           1       0.05      0.57      0.09      2503

    accuracy                           0.59     71250
   macro avg       0.51      0.58      0.41     71250
weighted avg       0.94      0.59      0.71     71250



##### <span style="color:MediumSlateBlue">Анализ влияния scaler преобразования на качество и скорость схождения модели</span>

In [321]:
# формируем список из необходимых scaler
scalers = [MinMaxScaler(),RobustScaler() ,StandardScaler()]

# сформируем списко для заполнения данными результатов анализа
scalers_data = []

# установим ограничение на время обучения модели в 600 секунд (10 минут)
time_out = 600

for scaler in scalers:
        # для того чтобы следить за выполнением цикла введем индикатор
        print('current scaler: ', scaler)

         # сформируем список для заполнения данными текушего scaler
        current_scaler_data = [scaler]
        
        # выполним scaler преобразование
        X_train_s_balanced = scaler.fit_transform(np.array(X_train_balanced)[:,list_n_last_features])
        X_train_s = scaler.transform(X_train[:,list_n_last_features])
        X_valid_s = scaler.transform(X_valid[:,list_n_last_features])

        try:
                # для модуля func_time_out упакуем обучение модели в функцию try_func
                def try_func():
                        logistic_regression = linear_model.LogisticRegression(random_state=42, max_iter=10000)
                        return logistic_regression.fit(X_train_s_balanced,y_train_balanced)
                    
                # фиксируем время начала
                start_time = time.time()
                
                # запускаем обучение модели с ограничением по времени
                logistic_regression = func_timeout.func_timeout(time_out, try_func)
                
                # фиксируем время окончания обучения
                end_time = time.time()
                
                # запишем время обучения модели
                current_scaler_data.append(round(end_time-start_time))

                # Делаем предсказание для обучающей и валидационной выборки
                y_valid_lr_pred = logistic_regression.predict(X_valid_s)
                
                # для метрик ROC AUC делаем предсказание модели для обучающей и валидационной выборки  
                # в виде вероятности принадлежности к классу 1 
                y_train_lr_pred_proba = logistic_regression.predict_proba(X_train_s)[:,1]
                y_valid_lr_pred_proba = logistic_regression.predict_proba(X_valid_s)[:,1]

                #Считаем метрики ROC AUC yна обуающем и валидационном наборе и добавляем их в спискок
                current_scaler_data.append(round(metrics.roc_auc_score(y_train, y_train_lr_pred_proba),3))
                current_scaler_data.append(round(metrics.roc_auc_score(y_valid, y_valid_lr_pred_proba),3))

                #Считаем метрики для класса 0 на валидационном наборе и добавляем их в список
                current_scaler_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))
                current_scaler_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))


                #Считаем метрики для класса 1 на валидационном набопе и добавляем их в список
                current_scaler_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))
                current_scaler_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))

                # добавляем полученные данные в список scalers_data
                scalers_data.append(current_scaler_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                scaler_pd =pd.DataFrame(
                        columns=['scaler','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = scalers_data)
                # сохраняем dataframe
                scaler_pd.to_csv('data_recovery/scaler_pd.csv',index=False)
               
                # очистим output от прошедшей итерации
                clear_output()

        except func_timeout.FunctionTimedOut:
                # если время обучения привышает лимит
                # запишем в current_scaler_data соотвествующую данные
                current_scaler_data = [scaler,'>30m',0,0,0,0,0,0]
                # добавляем полученные данные в список scalers_data
                scalers_data.append(current_scaler_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                scaler_pd =pd.DataFrame(
                        columns=['scaler','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = scalers_data)
                # сохраняем dataframe
                scaler_pd.to_csv('data_recovery/scaler_pd.csv',index=False)
                
                # очистим output от прошедшей итерации
                clear_output()
                # переходим к следующему scaler
                pass
# очистим output
clear_output()

# сформируем данные соотвествующие лучщему ROC AUC на валидацинном наборе
best_roc_valid_data = scaler_pd[scaler_pd['roc_valid']==scaler_pd['roc_valid'].max()]

# выведем лучший результат на валидационном наборе
print('result:')
print('best scaler on valid:',best_roc_valid_data.iloc[0]['scaler'])
print('ROC AUC on train:', best_roc_valid_data.iloc[0]['roc_train'])
print('ROC AUC on valid:', best_roc_valid_data.iloc[0]['roc_valid'])
print('Time fit for best scaler:', best_roc_valid_data.iloc[0]['time_fit'],' seconds')

# выведем полученный dataframe
scaler_pd

# time: 

result:
best scaler on valid: MinMaxScaler()
ROC AUC on train: 0.603
ROC AUC on valid: 0.611
Time fit for best scaler: 0  seconds


scaler  time_fit  roc_train  roc_valid  recall_0  precision_0  \
0    MinMaxScaler()         0      0.603      0.611     0.592        0.974   
1    RobustScaler()         0      0.603      0.610     0.592        0.974   
2  StandardScaler()         0      0.603      0.610     0.592        0.974   

   recall_1  precision_1  
0     0.573        0.049  
1     0.574        0.049  
2     0.573        0.049

##### <span style="color:MediumSlateBlue"> Анализ влияния solver оптимизатора на качество и скорость обучения модели</span>

Проверим качество и скорость сходимости модели при разных solver  
Проверку осуществим через цикл  
Чтобы модель не сходилась бесконечно с помощью модуля func_timeout  
поставим ограничение времени схождения в 10 минут

In [322]:
# подготовим данные для обучения модели

# обьявим scaler
scaler = StandardScaler()
# выполним scaler преобразование
X_train_s_balanced = scaler.fit_transform(np.array(X_train_balanced)[:,list_n_last_features])
X_train_s = scaler.transform(X_train[:,list_n_last_features])
X_valid_s = scaler.transform(X_valid[:,list_n_last_features])

# time: 10s

In [323]:
# Зададим список solvers
solvers_list = ['lbfgs', 'liblinear', 'newton-cg', 'newton-cholesky', 'sag', 'saga']

# сформируем список для заполнения
solvers_data = []

# установим ограничение на время обучения модели в 300 секунд (5 минут)
time_out = 300

for solver in solvers_list:
        # для того чтобы следить за выполнением цикла введем индикатор
        print('current solver: ', solver)

         # сформируем список для заполнения данными текушего solver
        current_solver_data = [solver]
        
        try:
                # для модуля func_time_out упакуем обучение модели в функцию try_func
                def try_func():
                        logistic_regression = linear_model.LogisticRegression(solver= solver,
                                                                  random_state=42, 
                                                                  max_iter=10000)
                        return logistic_regression.fit(X_train_s_balanced,y_train_balanced)
                    
                # фиксируем время начала
                start_time = time.time()
                
                # запускаем обучение модели с ограничением по времени
                logistic_regression = func_timeout.func_timeout(time_out, try_func)
                
                # фиксируем время окончания обучения
                end_time = time.time()
                
                # запишем время обучения модели
                current_solver_data.append(round(end_time-start_time))

                # Делаем предсказание для обучающей и валидационной выборки
                y_valid_lr_pred = logistic_regression.predict(X_valid_s)
                
                # для метрик ROC AUC делаем предсказание модели для обучающей и валидационной выборки  
                # в виде вероятности принадлежности к классу 1 
                y_train_lr_pred_proba = logistic_regression.predict_proba(X_train_s)[:,1]
                y_valid_lr_pred_proba = logistic_regression.predict_proba(X_valid_s)[:,1]

                #Считаем метрики ROC AUC yна обуающем и валидационном наборе и добавляем их в спискок
                current_solver_data.append(round(metrics.roc_auc_score(y_train, y_train_lr_pred_proba),3))
                current_solver_data.append(round(metrics.roc_auc_score(y_valid, y_valid_lr_pred_proba),3))

                #Считаем метрики для класса 0 на валидационном наборе и добавляем их в список
                current_solver_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))
                current_solver_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))


                #Считаем метрики для класса 1 на валидационном набопе и добавляем их в список
                current_solver_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))
                current_solver_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))

                # запишем данные полученные на одной итерации
                solvers_data.append(current_solver_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                solvers_pd =pd.DataFrame(
                        columns=['solver','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = solvers_data)
                # сохраняем dataframe
                solvers_pd.to_csv('data_recovery/solvers_pd.csv',index=False)
               
                # очистим output от прошедшей итерации
                clear_output()

        except func_timeout.FunctionTimedOut:
                # если время обучения привышает лимит
                # запишем в current_solver_data соотвествующую данные
                current_solver_data = [solver,'>10m',0,0,0,0,0,0]
                # добавляем полученные данные в список solvers_data
                solvers_data.append(current_solver_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                solvers_pd =pd.DataFrame(
                        columns=['solver','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = solvers_data)
                # сохраняем dataframe
                solvers_pd.to_csv('data_recovery/solvers_pd.csv',index=False)
                
                # очистим output от прошедшей итерации
                clear_output()
                # переходим к следующему solver
                pass
# очистим output
clear_output()

# сформируем данные соотвествующие лучщему ROC AUC на валидацинном наборе
best_roc_valid_data = solvers_pd[solvers_pd['roc_valid']==solvers_pd['roc_valid'].max()]

# выведем лучший результат на валидационном наборе
print('result:')
print('best solver on valid:',best_roc_valid_data.iloc[0]['solver'])
print('ROC AUC on train:', best_roc_valid_data.iloc[0]['roc_train'])
print('ROC AUC on valid:', best_roc_valid_data.iloc[0]['roc_valid'])
print('Time fit for best solver:', best_roc_valid_data.iloc[0]['time_fit'],' seconds')

# выведем полученный dataframe
solvers_pd

# time: 11m 35s

result:
best solver on valid: lbfgs
ROC AUC on train: 0.603
ROC AUC on valid: 0.61
Time fit for best solver: 0  seconds


solver  time_fit  roc_train  roc_valid  recall_0  precision_0  \
0            lbfgs         0      0.603       0.61     0.592        0.974   
1        liblinear         0      0.603       0.61     0.592        0.974   
2        newton-cg         0      0.603       0.61     0.592        0.974   
3  newton-cholesky         0      0.603       0.61     0.592        0.974   
4              sag         0      0.603       0.61     0.592        0.974   
5             saga         0      0.603       0.61     0.592        0.974   

   recall_1  precision_1  
0     0.573        0.049  
1     0.574        0.049  
2     0.575        0.049  
3     0.574        0.049  
4     0.574        0.049  
5     0.574        0.049

##### <span style="color:MediumSlateBlue">Подбор гиперпараметров модели</span>

In [1562]:
# для выбора sceler преобразвания на понадобится словарь
dict_scalers ={
    'MinMaxScaler':MinMaxScaler(),
    'RobustScaler':RobustScaler(),
    'StandardScaler':StandardScaler(),
}
# определим пространство признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'relative'
count_features = dict_spaces[feature_space]

# настроим оптимизацию гипер параметров
def optuna_lg(trial):
  # задаем пространства поиска гиперпараметров
  C = trial.suggest_float('C',0.01,1)
  solver = trial.suggest_categorical('solver', ['lbfgs', 'liblinear', 'newton-cg', 'newton-cholesky'])
  class_0_weight = trial.suggest_float('class_0_weight',0.01,1)
  class_1_weight = trial.suggest_float('class_1_weight',0.01,1)
  n_last = trial.suggest_int('n_last', 10, 25,step = 1)
  class_1_percent = trial.suggest_float('class_1_percent',0.01,1)
  scaler = trial.suggest_categorical('scaler', ['MinMaxScaler', 'RobustScaler','StandardScaler'])
  random_state = trial.suggest_int('random_state', 1, 1000000)

  # создаем модель
  optuna_log_reg = linear_model.LogisticRegression(
      solver=solver,
      C=C,
      class_weight={0:class_0_weight,1:class_1_weight},
      random_state=random_state,
      max_iter=10000)

  # с помощью функции features_from_transform_data_torow извлечем  
  # из данных transform_data_torow
  # признаки сооствествующие n_last последним клиенским операциям
  list_n_last_features = features_from_transform_data_torow(n_last,count_features,25)

  # обьявим scaler
  scaler = dict_scalers[scaler]

  # загружаем обучующие наборы
  X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
  y_train_pd = pd.read_csv('target/target_train.csv')

  # поготовим данные y_train_pd к работе с функцией class_1_percent_samples
  y_train_pd.set_index('id',drop=False,inplace=True)

  # подготовим данные для обучения модели
  # с помощью функции class_1_percent_samples зададим долю 
  # класса 1
  list_c1_percent_id = class_1_percent_samples(y_train_pd,class_1_percent,random_state=random_state)[:1000000]

  # сформируем данные для обучения базовой модели
  X_train_s_balanced = scaler.fit_transform(np.array(X_train_pd.loc[list_c1_percent_id])[:,list_n_last_features])
  y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

  # освободим память от "тяжелых" и ненужных файлов
  del X_train_pd, y_train_pd
  gc.collect()

  # я не воспользовался параметром timeout метода optimize потому, что  
  # optimize отставливает поиск параметров, если время обучения 
  # превышает timeout. Мне нужно чтобы поиск параметров продолжился.
  try:
    # для модуля func_time_out упакуем обучение модели в функцию try_func
    def try_func():
            return optuna_log_reg.fit(X_train_s_balanced, y_train_balanced)
    # обучаем модель с ограничением по времени 10 минут (600 секунд)
    optuna_log_reg = func_timeout.func_timeout(600, try_func)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train_s_balanced,y_train_balanced
    gc.collect()

    # подгружаем данные для тестирования
    X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()[:,list_n_last_features]
    y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
    X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()[:,list_n_last_features]
    y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

    # сформируем данные для проверки модели
    X_train_s = scaler.transform(X_train)
    X_valid_s = scaler.transform(X_valid)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train, X_valid
    gc.collect()

    # делаем предсказание на обучающем и валидационном наборе и считаем метрики
    roc_train = metrics.roc_auc_score(y_train, optuna_log_reg.predict_proba(X_train_s)[:,1])
    roc_valid = metrics.roc_auc_score(y_valid, optuna_log_reg.predict_proba(X_valid_s)[:,1])
    f1_score = metrics.f1_score(y_valid, optuna_log_reg.predict(X_valid_s))
    recall_1 = metrics.recall_score(y_valid, optuna_log_reg.predict(X_valid_s),average=None,zero_division=0)[1]
    precision_1 = metrics.precision_score(y_valid, optuna_log_reg.predict(X_valid_s),average=None,zero_division=0)[1]

    del X_train_s, X_valid_s, y_train, y_valid
    gc.collect()

  except func_timeout.FunctionTimedOut:
    # освободим память от "тяжелых" и ненужных файлов
    del X_train_s_balanced, y_train_balanced
    gc.collect()

    # обьявим метрики пустыми значениями
    roc_train = 0
    roc_valid = 0
    f1_score = 0
    recall_1 = 0
    precision_1 = 0
    pass

  return roc_train, roc_valid, f1_score, recall_1, precision_1

In [1563]:
# cоздаем объект исследования
# чтобы модель не переобучалась минимизируем roc_train 
# и максимизируем roc_valid
optuna_study_lg = optuna.create_study(study_name='LogisticRegression_'+feature_space+'_torow', 
                               directions=['maximize','maximize','maximize','maximize','maximize'], 
                               sampler=optuna.samplers.TPESampler(),
                               pruner='Hyperband',
                               storage='sqlite:///optuna_studies.db',
                               load_if_exists=True)
# на случай удаления 
# optuna.delete_study(study_name='LogisticRegression_'+feature_space+'_torow', storage='sqlite:///optuna_studies.db')

[I 2025-04-19 14:10:04,375] Using an existing study with name 'LogisticRegression_relative_torow' instead of creating a new one.


In [326]:
# ищем лучшую комбинацию гиперпараметров n_trials раз
optuna_study_lg.optimize(optuna_lg, n_trials=300)

[I 2025-04-17 13:39:12,408] Trial 0 finished with values: [0.6056333770524716, 0.6121216746255316, 0.09659931000492854, 0.23491809828206153, 0.06080033088615448] and parameters: {'C': 0.16503964681569627, 'solver': 'newton-cholesky', 'class_0_weight': 0.6222956553551775, 'class_1_weight': 0.9770083218715612, 'n_last': 11, 'class_1_percent': 0.31164904079850647, 'scaler': 'RobustScaler', 'random_state': 264988}.
[I 2025-04-17 13:39:15,640] Trial 1 finished with values: [0.6086360917505488, 0.6153010557258706, 0.08597955839900133, 0.6604075109868158, 0.0459830866807611] and parameters: {'C': 0.12052793959442595, 'solver': 'newton-cholesky', 'class_0_weight': 0.1693083272755873, 'class_1_weight': 0.4611538953911282, 'n_last': 20, 'class_1_percent': 0.2866927818965846, 'scaler': 'StandardScaler', 'random_state': 343060}.
[I 2025-04-17 13:39:18,776] Trial 2 finished with values: [0.6066263556069124, 0.6122727435791613, 0.06804134988787398, 0.9940071913703555, 0.035226323464865705] and param

In [1564]:
# из полученного результат соврмируем Data Frame
optuna_study_lg_pd = optuna_study_lg.trials_dataframe().dropna()
# переименуем столбы
optuna_study_lg_pd.rename(columns={
    'values_0': 'roc_train',
    'values_1': 'roc_valid',
    'values_2': 'f1_score',
    'values_3': 'recall_1',
    'values_4': 'precision_1'
},inplace=True)
# Выделим время потраченное на обучение модели
optuna_study_lg_pd.head(5)

number  roc_train  roc_valid  f1_score  recall_1  precision_1  \
0       0   0.605633   0.612122  0.096599  0.234918     0.060800   
1       1   0.608636   0.615301  0.085980  0.660408     0.045983   
2       2   0.606626   0.612273  0.068041  0.994007     0.035226   
3       3   0.606967   0.614491  0.000000  0.000000     0.000000   
4       4   0.563228   0.572639  0.067875  1.000000     0.035130   

              datetime_start          datetime_complete  \
0 2025-04-17 13:39:09.329673 2025-04-17 13:39:12.404480   
1 2025-04-17 13:39:12.411658 2025-04-17 13:39:15.637175   
2 2025-04-17 13:39:15.642921 2025-04-17 13:39:18.774057   
3 2025-04-17 13:39:18.779510 2025-04-17 13:39:21.943334   
4 2025-04-17 13:39:21.949044 2025-04-17 13:39:24.877672   

                duration  params_C  params_class_0_weight  \
0 0 days 00:00:03.074807  0.165040               0.622296   
1 0 days 00:00:03.225517  0.120528               0.169308   
2 0 days 00:00:03.131136  0.177788               0.062083   
3 0 days 00:00:03.163824  0.199942               0.321277   
4 0 days 00:00:02.928628  0.038404               0.158416   

   params_class_1_percent  params_class_1_weight  params_n_last  \
0                0.311649               0.977008             11   
1                0.286693               0.461154             20   
2                0.169625               0.682544             13   
3                0.439089               0.036761             23   
4                0.989120               0.208672             17   

   params_random_state   params_scaler    params_solver     state  
0               264988    RobustScaler  newton-cholesky  COMPLETE  
1               343060  StandardScaler  newton-cholesky  COMPLETE  
2               937971  StandardScaler  newton-cholesky  COMPLETE  
3               536876    MinMaxScaler  newton-cholesky  COMPLETE  
4               581964    RobustScaler        newton-cg  COMPLETE

In [1565]:
# покаждем статистику обучения
print('Максимальное значение метрики ROC AUC на валидационном наборе:',round(optuna_study_lg_pd['roc_valid'].max(),3))
print('Среднее значение метрики ROC AUC на валидационном наборе:',round(optuna_study_lg_pd['roc_valid'].mean(),3))
print('Максимальное значение метрики f1_score на валидационном наборе:',round(optuna_study_lg_pd['f1_score'].max(),3))
print('Среднее значение метрики f1_score на валидационном наборе:',round(optuna_study_lg_pd['f1_score'].mean(),3))
print('Максимальное значение метрики recall_1 на валидационном наборе:',round(optuna_study_lg_pd['recall_1'].max(),3))
print('Среднее значение метрики recall_1 на валидационном наборе:',round(optuna_study_lg_pd['recall_1'].mean(),3))
print('Максимальное значение метрики precision_1 на валидационном наборе:',round(optuna_study_lg_pd['precision_1'].max(),3))
print('Среднее значение метрики precision_1 на валидационном наборе:',round(optuna_study_lg_pd['precision_1'].mean(),3))

Максимальное значение метрики ROC AUC на валидационном наборе: 0.618
Среднее значение метрики ROC AUC на валидационном наборе: 0.614
Максимальное значение метрики f1_score на валидационном наборе: 0.101
Среднее значение метрики f1_score на валидационном наборе: 0.074
Максимальное значение метрики recall_1 на валидационном наборе: 1.0
Среднее значение метрики recall_1 на валидационном наборе: 0.487
Максимальное значение метрики precision_1 на валидационном наборе: 0.333
Среднее значение метрики precision_1 на валидационном наборе: 0.059


In [1568]:
# Визуализируем метрики полученные при optuna оптимизации
fig = px.scatter(
    data_frame=optuna_study_lg_pd[(optuna_study_lg_pd['roc_valid']>0.998*optuna_study_lg_pd['roc_valid'].max())&
                                  (optuna_study_lg_pd['f1_score']>0.99*optuna_study_lg_pd['f1_score'].max())],
    x='number', #ось абсцисс
    y=['roc_train','roc_valid','recall_1','precision_1','f1_score'], #ось ординат
)
fig.update_layout(
    title ={
        'text':'Зависимость качества модели от trials optuna', # Имя рабочей плоскости
        'font':{'size':35,'family':"Times New Roman"}, # размер и стиль написания имени рабочей плоскости
        'x':0.5, # Смешение имени по оси "x" на половину рабочей плоскости
        },
    height =800,# Высота рабочей плоскости
    width = 1350, # Ширина рабочей плоскости
    bargap=0.2, # Добавил расстояния между столбами гистограммы
    xaxis_title='trials optuna',
    yaxis_title='Величина метрики')
fig.update_xaxes(showspikes=True)
fig.update_yaxes(showspikes=True)

fig.show()

<span style="color:Blue">

Вывод:  

Их всех выбираем точку $number =220$.   
В этой точке одно из самых больших значений $ROC AUC$.  
Посмотрим каким значениям гиперпараметров соотвествует выбранная точка.

In [1569]:
# определим номер лучшге варианта
best_optuna_number = 220

# сформируем словарь лучших гипирпарметров RandomForestClassifier
best_param_lr_torow = {
    'C' : round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_C'].iloc[0],3),
    'class_weight' : {0:round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_class_0_weight'].iloc[0],3),
                      1:round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_class_1_weight'].iloc[0],3)},
    }
# создадим перменные
best_n_last = int(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_n_last'].iloc[0])
best_scaler = optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_scaler'].iloc[0]
best_class_1_percent = optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_class_1_percent'].iloc[0]
best_random_state = int(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_random_state'].iloc[0])
# Выведем принятые наилучшие праметры
print('best C:',best_param_lr_torow['C'])
print('best class 0 weight:',best_param_lr_torow['class_weight'][0])
print('best class 1 weight:',best_param_lr_torow['class_weight'][1])

print('best class 1 percent:',round(best_class_1_percent,3))
print('best scaler:',best_scaler)
print('best n_last:',round(best_n_last,3))
print('best best random state:',best_random_state)
print('time for best train:',round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['duration'].iloc[0].seconds/60),'minutes')

print()
print('ROC AUC на обучающем наборе:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['roc_train'].iloc[0],3))
print('ROC AUC на валидационном наборе:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['roc_valid'].iloc[0],3))
print('precision класса 1:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['precision_1'].iloc[0],3))
print('recall класса 1:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['recall_1'].iloc[0],3))

best C: 0.423
best class 0 weight: 0.926
best class 1 weight: 0.79
best class 1 percent: 0.431
best scaler: StandardScaler
best n_last: 23
best best random state: 869631
time for best train: 0 minutes

ROC AUC на обучающем наборе: 0.608
ROC AUC на валидационном наборе: 0.617
precision класса 1: 0.068
recall класса 1: 0.191


##### <span style="color:MediumSlateBlue">Обучение модели с лучшими параметрами</span>

In [1570]:
# для выбора sceler преобразвания на понадобится словарь
dict_scalers ={
    'MinMaxScaler':MinMaxScaler(),
    'RobustScaler':RobustScaler(),
    'StandardScaler':StandardScaler(),
}

# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'relative'
count_features = dict_spaces[feature_space]

# с помощью функции features_from_transform_data_torow извлечем  
# из данных transform_data_torow_25
# признаки сооствествующие n_last последним клиенским операциям
list_n_last_features = features_from_transform_data_torow(best_n_last,count_features,25)

# обьявим scaler
scaler = dict_scalers[best_scaler]

# загружаем обучующие наборы
X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)

# подготовим данные для обучения модели
# с помощью функции class_1_percent_samples зададим долю 
# класса 1
list_c1_percent_id = class_1_percent_samples(y_train_pd,best_class_1_percent,random_state=best_random_state)[:1000000]

# сформируем данные для обучения базовой модели
X_train_s_balanced = scaler.fit_transform(np.array(X_train_pd.loc[list_c1_percent_id])[:,list_n_last_features])
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

# освободим память от "тяжелых" и ненужных файлов
del X_train_pd, y_train_pd
gc.collect()


# обучаем модель LogisticRegression с наилучшеми параметрами
logistic_regression = linear_model.LogisticRegression(
        **best_param_lr_torow,
        random_state=best_random_state,
        max_iter=10000)
logistic_regression.fit(X_train_s_balanced,y_train_balanced)

# удаляем крупные файлы чтобы высвободить память 
del X_train_s_balanced,y_train_balanced
gc.collect()

# подгружаем данные для тестирования
X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()[:,list_n_last_features]
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()[:,list_n_last_features]
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()
    
# сформируем данные для проверки модели
X_train_s = scaler.transform(X_train)
X_valid_s = scaler.transform(X_valid)

# удаляем крупные файлы чтобы высвободить память 
del X_train, X_valid
gc.collect()

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_lr_pred_proba = logistic_regression.predict_proba(X_train_s)[:,1]
y_valid_lr_pred_proba = logistic_regression.predict_proba(X_valid_s)[:,1]

# Делаем предсказание для валидационной выборки
y_valid_lr_pred = logistic_regression.predict(X_valid_s)

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_lr_pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_lr_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_lr_pred,zero_division=0))

# time: 2m 40s

ROC AUC на обучающем наборе 0.608
ROC AUC на валидационном наборе 0.617
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.97      0.90      0.94     68747
           1       0.07      0.19      0.10      2503

    accuracy                           0.88     71250
   macro avg       0.52      0.55      0.52     71250
weighted avg       0.94      0.88      0.91     71250



#### <span style="color:MediumBlue">Построение модели Random Forest Classifier</span>

##### <span style="color:MediumSlateBlue">Формирование данных для обучения</span>

Анализ исходных данных, в частности target, показал что представленные данные   
имееют перекос: 96% клиентов у которых не случился дефолт (flag = 0),    
против 4 % - для которых произошел дефолт (flag = 1).  
С помощью функции class_1_percent_samples, сформируем сбаланисрованную выборку  
для обучения моделей.
За основу сбалансировных данных возьмем данные клиентов с дефолтом  
и к ним будем добирать необходимое количество клиентов до сбалансированности. 


Функция class_1_percent_samples принемает две переменные:
- target_data - массив с id и целевой переменной
- class_1_percent - процент класса 1 в результирующем массиве

In [344]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'relative'
count_features = dict_spaces[feature_space]

In [345]:
# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

In [346]:
# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)
y_train_pd.head(4)

id  flag
id                    
1825800  1825800     0
2166483  2166483     0
2534345  2534345     0
1803283  1803283     0

In [347]:
# взглянем на сблансиорованность данных в y_train
y_train_pd['flag'].value_counts(normalize=True)

flag
0    0.964242
1    0.035758
Name: proportion, dtype: float64

In [348]:
# сбалансируем данные в y_train_pd
list_c1_percent_id = class_1_percent_samples(y_train_pd,0.5)
# list_c1_percent_features - список 'id' из y_train_pd соотвествующих  
# заданному проценту класса 1
len(list_c1_percent_id)

45860

In [349]:
# проверим сбалансированность полученного y_train
y_train_pd.loc[list_c1_percent_id]['flag'].value_counts(normalize=True)

flag
1    0.5
0    0.5
Name: proportion, dtype: float64

*transform_data_torow*, показываеются последние N операций клиента.  
В данных в *date_torow*, собраны последние 25 операций клиентов.

Предварительный анализ показывает, что медиальное значение количества клиентских  
операций равно 7. Поэтому, для начала, будем показывать моделе $n_{last} = 7$   
последних клиентских операций.

Для извлечения из *transform_data_torow_25* необходимого количества последних клиенских  
операций ($n_{last}$) используем функцию features_from_transform_data_torow.

Функция features_from_transform_data_torow примает следующие аргументы:
- $n_{last} = 7$ - необходимое количество последних клиентских операций; 
- $n_{groups} = 8$ - количество признаков в $date$ $features$;
- $N_{last} = 25$ - количество $n_{last}$ операций, показанных в transform_data_torow_25


In [350]:
# с помощью функции features_from_transform_data_torow извлечем  
# из данных transform_data_torow_25
# признаки сооствествующие 7 последним клиенским операциям
list_n_last_features = features_from_transform_data_torow(7,count_features,25)

In [351]:
# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']
# сформируем данные для проверики модели
X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

In [352]:
# посмотрим на структуру данных в X_train_balanced
X_train_balanced.head(2)

f1  f2  f3  f4  f5  f6  f7  f8  f9  f10  ...  f141  f142  f143  f144  \
id                                                ...                           
2335465   6  11  16  16  16  16  16  16  16   16  ...     1     1     0     0   
390270   15  11   0  16  16  16   0   0   0    0  ...     0     0     0     0   

         f145  f146  f147  f148  f149  f150  
id                                           
2335465     0     0     0     0     0     0  
390270      0     0     0     0     0     0  

[2 rows x 150 columns]

In [353]:
# посмотрим на структуру данных в y_train_balanced
y_train_balanced.head(2)

id
2335465    1
390270     1
Name: flag, dtype: int64

In [354]:
# проверим что выборки действительно совпадают по id
X_train_balanced.index.to_list() == y_train_balanced.index.to_list()

True

##### <span style="color:MediumSlateBlue">Baseline обучение модели RandomForestClassifier</span>

In [355]:
# обучаем модель логистической регрессии
# чтобы модель пыталась найти связь во всех признаках
random_forest = RandomForestClassifier(random_state=42, n_jobs=-1)
random_forest.fit(np.array(X_train_balanced)[:,list_n_last_features],np.array(y_train_balanced))

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_rf__pred_proba = random_forest.predict_proba(X_train[:,list_n_last_features])[:,1]
y_valid_rf_pred_proba = random_forest.predict_proba(X_valid[:,list_n_last_features])[:,1]

# Делаем предсказание для валидационной выборки
y_valid_rf_pred = random_forest.predict(X_valid[:,list_n_last_features])

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_rf__pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_rf_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_rf_pred))

# time: 2m 5s

ROC AUC на обучающем наборе 0.832
ROC AUC на валидационном наборе 0.602
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.97      0.56      0.71     68747
           1       0.05      0.60      0.09      2503

    accuracy                           0.56     71250
   macro avg       0.51      0.58      0.40     71250
weighted avg       0.94      0.56      0.69     71250



##### <span style="color:MediumSlateBlue">Подбор гиперпараметров модели</span>

In [1571]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'relative'
count_features = dict_spaces[feature_space]

# настроим оптимизацию гипер параметров
def optuna_rf(trial):
  # задаем пространства поиска гиперпараметров
  # задаем пространства поиска гиперпараметров
  n_estimators = trial.suggest_int('n_estimators', 50, 150,step = 5)
  criterion = trial.suggest_categorical('criterion',['gini', 'entropy', 'log_loss'])
  max_depth = trial.suggest_int('max_depth', 9, 20,step = 1)
  min_samples_split = trial.suggest_int('min_samples_split', 5, 15,step = 1)
  min_samples_leaf = trial.suggest_int('min_samples_leaf', 5, 25,step = 1)
  max_features = trial.suggest_float('max_features',0.1,1)
  max_samples = trial.suggest_float('max_samples',0.1,1)
  class_0_weight = trial.suggest_float('class_0_weight',0.01,1)
  class_1_weight = trial.suggest_float('class_1_weight',0.01,1)
  n_last = trial.suggest_int('n_last', 5, 25,step = 1)
  class_1_percent = trial.suggest_float('class_1_percent',0.01,1)
  random_state = trial.suggest_int('random_state', 1, 1000000)


  # создаем модель
  optuna_random_forest = RandomForestClassifier(
      n_estimators = n_estimators, 
      criterion = criterion,
      max_depth = max_depth,
      min_samples_split = min_samples_split,  
      min_samples_leaf = min_samples_leaf,
      max_features=max_features,
      max_samples=max_samples,
      class_weight={0:class_0_weight,1:class_1_weight},
      n_jobs=-1,
      random_state=random_state)

  # с помощью функции features_from_transform_data_torow извлечем  
  # из данных transform_data_torow
  # признаки сооствествующие n_last последним клиенским операциям
  list_n_last_features = features_from_transform_data_torow(n_last,count_features,25)

  # загружаем обучующие наборы
  X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
  y_train_pd = pd.read_csv('target/target_train.csv')

  # поготовим данные y_train_pd к работе с функцией class_1_percent_samples
  y_train_pd.set_index('id',drop=False,inplace=True)

  # подготовим данные для обучения модели
  # с помощью функции class_1_percent_samples зададим долю 
  # класса 1
  list_c1_percent_id = class_1_percent_samples(y_train_pd,class_1_percent,random_state=random_state)[:1000000]

  # сформируем данные для обучения базовой модели
  X_train_balanced = np.array(X_train_pd.loc[list_c1_percent_id])[:,list_n_last_features]
  y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

  # освободим память от "тяжелых" и ненужных файлов
  del X_train_pd, y_train_pd
  gc.collect()

  # я не воспользовался параметром timeout метода optimize потому, что  
  # optimize отставливает поиск параметров, если время обучения 
  # превышает timeout. Мне нужно чтобы поиск параметров продолжился.
  try:
    # для модуля func_time_out упакуем обучение модели в функцию try_func
    def try_func():
            return optuna_random_forest.fit(X_train_balanced,y_train_balanced)
    # обучаем модель с ограничением по времени 10 минут (600 секунд)
    optuna_random_forest = func_timeout.func_timeout(600, try_func)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train_balanced, y_train_balanced
    gc.collect()

    # подгружаем данные для тестирования
    X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()[:,list_n_last_features]
    y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
    X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()[:,list_n_last_features]
    y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

    # делаем предсказание на обучающем и валидационном наборе и считаем метрики
    roc_train = metrics.roc_auc_score(y_train, optuna_random_forest.predict_proba(X_train)[:,1])
    roc_valid = metrics.roc_auc_score(y_valid, optuna_random_forest.predict_proba(X_valid)[:,1])
    f1_score = metrics.f1_score(y_valid, optuna_random_forest.predict(X_valid))
    recall_1 = metrics.recall_score(y_valid, optuna_random_forest.predict(X_valid),average=None,zero_division=0)[1]
    precision_1 = metrics.precision_score(y_valid, optuna_random_forest.predict(X_valid),average=None,zero_division=0)[1]

    # удаляем крупные файлы чтобы высвободить память 
    del X_train, X_valid, y_train, y_valid 
    gc.collect()

  except func_timeout.FunctionTimedOut:
    # освободим память от "тяжелых" и ненужных файлов
    del X_train_balanced, y_train_balanced
    gc.collect()

    # обьявим метрики пустыми значениями
    roc_train = 0
    roc_valid = 0
    f1_score = 0
    recall_1 = 0
    precision_1 = 0
    pass

  return roc_train, roc_valid, f1_score, recall_1, precision_1

In [1572]:
# так как Random Forest склонен к переобучению 
# попробуем направить optimize в сторону уменьшения roc_train
# cоздаем объект исследования
optuna_study_rf = optuna.create_study(study_name='RandomForestClassifier_'+feature_space+'_torow', 
                               directions=['minimize','maximize','maximize','maximize','maximize'], 
                               sampler=optuna.samplers.TPESampler(),
                               pruner='Hyperband',
                               storage='sqlite:///optuna_studies.db',
                               load_if_exists=True)
# на случай удаления 
# optuna.delete_study(study_name='RandomForestClassifier_'+feature_space+'_torow', storage='sqlite:///optuna_studies.db')

[I 2025-04-19 14:12:21,782] Using an existing study with name 'RandomForestClassifier_relative_torow' instead of creating a new one.


In [358]:
# ищем лучшую комбинацию гиперпараметров n_trials раз
optuna_study_rf.optimize(optuna_rf, n_trials=300)

[I 2025-04-17 14:03:29,702] Trial 0 finished with values: [0.6739548822895425, 0.6429217808427842, 0.06982808022922636, 0.9736316420295645, 0.036212609774581336] and parameters: {'n_estimators': 65, 'criterion': 'log_loss', 'max_depth': 10, 'min_samples_split': 9, 'min_samples_leaf': 15, 'max_features': 0.9221592817927537, 'max_samples': 0.9649153809185963, 'class_0_weight': 0.4154802605548081, 'class_1_weight': 0.9451076632586721, 'n_last': 20, 'class_1_percent': 0.4669233805912821, 'random_state': 282081}.
[I 2025-04-17 14:03:34,532] Trial 1 finished with values: [0.6529458579419821, 0.6317159600778367, 0.06787520507640367, 1.0, 0.03512982456140351] and parameters: {'n_estimators': 130, 'criterion': 'entropy', 'max_depth': 17, 'min_samples_split': 7, 'min_samples_leaf': 16, 'max_features': 0.9329535980441455, 'max_samples': 0.3449543866239077, 'class_0_weight': 0.08464339016046755, 'class_1_weight': 0.31437155775565795, 'n_last': 19, 'class_1_percent': 0.8441077870633498, 'random_sta

In [1573]:
# из полученного результат соврмируем Data Frame
optuna_study_rf_pd = optuna_study_rf.trials_dataframe().dropna()
# переименуем столбы
optuna_study_rf_pd.rename(columns={
    'values_0': 'roc_train',
    'values_1': 'roc_valid',
    'values_2': 'f1_score',
    'values_3': 'recall_1',
    'values_4': 'precision_1'
},inplace=True)
optuna_study_rf_pd.sort_values(by='precision_1').drop(['datetime_start','datetime_complete','duration'],axis=1)

number  roc_train  roc_valid  f1_score  recall_1  precision_1  \
254     254   0.691158   0.649555  0.000000  0.000000     0.000000   
298     298   0.728556   0.648322  0.000000  0.000000     0.000000   
26       26   0.636660   0.634186  0.000000  0.000000     0.000000   
29       29   0.669063   0.647394  0.000000  0.000000     0.000000   
161     161   0.682132   0.645817  0.000000  0.000000     0.000000   
..      ...        ...        ...       ...       ...          ...   
147     147   0.616019   0.616306  0.002387  0.001199     0.272727   
92       92   0.665444   0.642699  0.010204  0.005194     0.288889   
48       48   0.708410   0.653675  0.010998  0.005593     0.325581   
218     218   0.625704   0.621827  0.010998  0.005593     0.325581   
194     194   0.624983   0.619561  0.004775  0.002397     0.600000   

     params_class_0_weight  params_class_1_percent  params_class_1_weight  \
254               0.611032                0.204542               0.223161   
298               0.679824                0.225908               0.049643   
26                0.763434                0.379547               0.026942   
29                0.423865                0.154664               0.111250   
161               0.768582                0.326064               0.030331   
..                     ...                     ...                    ...   
147               0.720902                0.728798               0.013396   
92                0.462251                0.523685               0.066198   
48                0.843131                0.225912               0.536918   
218               0.759867                0.686013               0.036651   
194               0.648467                0.543175               0.010417   

    params_criterion  params_max_depth  params_max_features  \
254          entropy                16             0.626161   
298             gini                17             0.894104   
26              gini                14             0.107048   
29              gini                11             0.841538   
161         log_loss                17             0.928892   
..               ...               ...                  ...   
147         log_loss                19             0.158463   
92          log_loss                19             0.862261   
48          log_loss                13             0.999708   
218         log_loss                11             0.309690   
194             gini                11             0.996332   

     params_max_samples  params_min_samples_leaf  params_min_samples_split  \
254            0.217682                       17                        15   
298            0.958905                       11                        12   
26             0.173065                       18                        14   
29             0.188352                       14                        13   
161            0.303845                        9                        12   
..                  ...                      ...                       ...   
147            0.125657                       10                        12   
92             0.449013                       23                        11   
48             0.424239                       11                        14   
218            0.112955                       12                        13   
194            0.104363                        8                        14   

     params_n_estimators  params_n_last  params_random_state     state  
254                  110             22               406707  COMPLETE  
298                  130             15               977865  COMPLETE  
26                   120              5               822589  COMPLETE  
29                    80              6               702673  COMPLETE  
161                   75              7               941453  COMPLETE  
..                   ...            ...                  ...       ...  
147                   80          

In [1574]:
# покаждем статистику обучения
print('Максимальное значение метрики ROC AUC на валидационном наборе:',round(optuna_study_rf_pd['roc_valid'].max(),3))
print('Среднее значение метрики ROC AUC на валидационном наборе:',round(optuna_study_rf_pd['roc_valid'].mean(),3))
print('Максимальное значение метрики f1_score на валидационном наборе:',round(optuna_study_rf_pd['f1_score'].max(),3))
print('Среднее значение метрики f1_score на валидационном наборе:',round(optuna_study_rf_pd['f1_score'].mean(),3))
print('Максимальное значение метрики recall_1 на валидационном наборе:',round(optuna_study_rf_pd['recall_1'].max(),3))
print('Среднее значение метрики recall_1 на валидационном наборе:',round(optuna_study_rf_pd['recall_1'].mean(),3))
print('Максимальное значение метрики precision_1 на валидационном наборе:',round(optuna_study_rf_pd['precision_1'].max(),3))
print('Среднее значение метрики precision_1 на валидационном наборе:',round(optuna_study_rf_pd['precision_1'].mean(),3))

Максимальное значение метрики ROC AUC на валидационном наборе: 0.654
Среднее значение метрики ROC AUC на валидационном наборе: 0.632
Максимальное значение метрики f1_score на валидационном наборе: 0.116
Среднее значение метрики f1_score на валидационном наборе: 0.066
Максимальное значение метрики recall_1 на валидационном наборе: 1.0
Среднее значение метрики recall_1 на валидационном наборе: 0.515
Максимальное значение метрики precision_1 на валидационном наборе: 0.6
Среднее значение метрики precision_1 на валидационном наборе: 0.06


In [1578]:
# Построим зависимость метрик качества модели от number

fig = px.scatter(
    data_frame=optuna_study_rf_pd[(optuna_study_rf_pd['roc_valid']>=0.65)&
                                  (optuna_study_rf_pd['f1_score']>=0.9*optuna_study_rf_pd['f1_score'].max())],
    x='number', #ось абсцисс
    y=['roc_valid','roc_train','precision_1','recall_1','f1_score'], #ось ординат
)
fig.update_layout(
    title ={
        'text':'Зависимость метрик качества модели от number', # Имя рабочей плоскости
        'font':{'size':35,'family':"Times New Roman"}, # размер и стиль написания имени рабочей плоскости
        'x':0.5, # Смешение имени по оси "x" на половину рабочей плоскости
        },
    height =800,# Высота рабочей плоскости
    width = 1350, # Ширина рабочей плоскости
    bargap=0.2, # Добавил расстояния между столбами гистограммы
    xaxis_title='Величина метрики ROC Valid',
    yaxis_title='Величина параметра')
fig.update_xaxes(showspikes=True)
fig.update_yaxes(showspikes=True)

fig.show()

In [1579]:
# определим номер лучшге варианта
best_optuna_number = 234

# сформируем словарь лучших гипирпарметров RandomForestClassifier
best_param_rf = {
    'n_estimators' : int(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_n_estimators'].iloc[0]),
    'criterion': optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_criterion'].iloc[0],
    'max_depth' : optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_max_depth'].iloc[0],
    'min_samples_split': optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_min_samples_split'].iloc[0],
    'min_samples_leaf' : optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_min_samples_leaf'].iloc[0],
    'max_features': optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_max_features'].iloc[0],
    'max_samples' : optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_max_samples'].iloc[0],
    'class_weight' : {0:optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_class_0_weight'].iloc[0],
                      1:optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_class_1_weight'].iloc[0]}
    }
# определим перменные для лучших значений параметров
best_n_last = optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_n_last'].iloc[0]
best_class_1_percent = optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_class_1_percent'].iloc[0]
best_random_state = optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_random_state'].iloc[0]


# Выведем принятые наилучшие праметры
print('best n estimators:',best_param_rf['n_estimators'])
print('best criterion:',best_param_rf['criterion'])
print('best max depth:',best_param_rf['max_depth'])
print('best min samples split:',best_param_rf['min_samples_split'])
print('best min samples leaf:',best_param_rf['min_samples_leaf'])
print('best max features(%):',round(best_param_rf['max_features'],3))
print('best max samples(%):',round(best_param_rf['max_samples'],3))
print('best class 0 weight:',round(best_param_rf['class_weight'][0],3))
print('best class 1 weight:',round(best_param_rf['class_weight'][1],3))

print('best class 1 percent:',round(best_class_1_percent,3))
print('best n last:',best_n_last)
print('best random state:',best_random_state)
print('time for best train:',round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['duration'].iloc[0].seconds/60),'minutes')

print()
print('ROC AUC на обучающем наборе:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['roc_train'].iloc[0],3))
print('ROC AUC на валидационном наборе:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['roc_valid'].iloc[0],3))
print('precision класса 1:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['precision_1'].iloc[0],3))
print('recall класса 1:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['recall_1'].iloc[0],3))

best n estimators: 125
best criterion: gini
best max depth: 11
best min samples split: 15
best min samples leaf: 20
best max features(%): 0.821
best max samples(%): 0.461
best class 0 weight: 0.581
best class 1 weight: 0.802
best class 1 percent: 0.265
best n last: 23
best random state: 2263
time for best train: 0 minutes

ROC AUC на обучающем наборе: 0.682
ROC AUC на валидационном наборе: 0.651
precision класса 1: 0.094
recall класса 1: 0.119


##### <span style="color:MediumSlateBlue">Обучение модели с лучшими параметрами</span>

In [1580]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'relative'
count_features = dict_spaces[feature_space]

# с помощью функции features_from_transform_data_torow извлечем  
# из данных transform_data_torow
# признаки сооствествующие n_last последним клиенским операциям
list_n_last_features = features_from_transform_data_torow(best_n_last,count_features,25)

# загружаем обучующие наборы
X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)

# подготовим данные для обучения модели
# с помощью функции class_1_percent_samples зададим долю 
# класса 1
list_c1_percent_id = class_1_percent_samples(y_train_pd,best_class_1_percent,random_state=best_random_state)[:1000000]

# сформируем данные для обучения базовой модели
X_train_balanced = np.array(X_train_pd.loc[list_c1_percent_id])[:,list_n_last_features]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

# освободим память от "тяжелых" и ненужных файлов
del X_train_pd, y_train_pd
gc.collect()

# обучаем модель RandomForestClassifier с наилучшеми параметрами
random_forest = RandomForestClassifier(
        **best_param_rf,
        n_jobs=-1,
        random_state=best_random_state)
random_forest.fit(X_train_balanced, y_train_balanced)

# освободим память от "тяжелых" и ненужных файлов
del X_train_balanced, y_train_balanced
gc.collect()


# подгружаем данные для тестирования
X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()[:,list_n_last_features]
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()[:,list_n_last_features]
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_rf__pred_proba = random_forest.predict_proba(X_train)[:,1]
y_valid_rf_pred_proba = random_forest.predict_proba(X_valid)[:,1]

# Делаем предсказание для валидационной выборки
y_valid_rf_pred = random_forest.predict(X_valid)

# удаляем крупные файлы чтобы высвободить память 
del X_train, X_valid
gc.collect()

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_rf__pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_rf_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_rf_pred,zero_division=0))

# time: 2m 10s

ROC AUC на обучающем наборе 0.682
ROC AUC на валидационном наборе 0.651
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.97      0.96      0.96     68747
           1       0.09      0.12      0.11      2503

    accuracy                           0.93     71250
   macro avg       0.53      0.54      0.53     71250
weighted avg       0.94      0.93      0.93     71250



#### <span style="color:MediumBlue">Построение модели Gradient Boosting Classifier</span>

##### <span style="color:MediumSlateBlue">Формирование данных для обучения</span>

Анализ исходных данных, в частности target, показал что представленные данные   
имееют перекос: 96% клиентов у которых не случился дефолт (flag = 0),    
против 4 % - для которых произошел дефолт (flag = 1).  
С помощью функции class_1_percent_samples, сформируем сбаланисрованную выборку  
для обучения моделей.
За основу сбалансировных данных возьмем данные клиентов с дефолтом  
и к ним будем добирать необходимое количество клиентов до сбалансированности. 


Функция class_1_percent_samples принемает две переменные:
- target_data - массив с id и целевой переменной
- class_1_percent - процент класса 1 в результирующем массиве

In [376]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'relative'
count_features = dict_spaces[feature_space]

In [377]:
# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

In [378]:
# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)
y_train_pd.head(4)

id  flag
id                    
1825800  1825800     0
2166483  2166483     0
2534345  2534345     0
1803283  1803283     0

In [379]:
# взглянем на сблансиорованность данных в y_train
y_train_pd['flag'].value_counts(normalize=True)

flag
0    0.964242
1    0.035758
Name: proportion, dtype: float64

In [380]:
# сбалансируем данные в y_train_pd
list_c1_percent_id = class_1_percent_samples(y_train_pd,0.5)
# list_c1_percent_features - список 'id' из y_train_pd соотвествующих  
# заданному проценту класса 1
len(list_c1_percent_id)

45860

In [381]:
# проверим сбалансированность полученного y_train
y_train_pd.loc[list_c1_percent_id]['flag'].value_counts(normalize=True)

flag
1    0.5
0    0.5
Name: proportion, dtype: float64

*transform_data_torow*, показываеются последние N операций клиента.  
В данных в *date_torow*, собраны последние 25 операций клиентов.

Предварительный анализ показывает, что медиальное значение количества клиентских  
операций равно 7. Поэтому, для начала, будем показывать моделе $n_{last} = 7$   
последних клиентских операций.

Для извлечения из *transform_data_torow_25* необходимого количества последних клиенских  
операций ($n_{last}$) используем функцию features_from_transform_data_torow.

Функция features_from_transform_data_torow примает следующие аргументы:
- $n_{last} = 7$ - необходимое количество последних клиентских операций; 
- $n_{groups} = 8$ - количество признаков в $date$ $features$;
- $N_{last} = 25$ - количество $n_{last}$ операций, показанных в transform_data_torow_25


In [382]:
# с помощью функции features_from_transform_data_torow извлечем  
# из данных transform_data_torow_25
# признаки сооствествующие 7 последним клиенским операциям
list_n_last_features = features_from_transform_data_torow(7,count_features,25)

In [383]:
# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']
# сформируем данные для проверики модели
X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

In [384]:
# посмотрим на структуру данных в X_train_balanced
X_train_balanced.head(2)

f1  f2  f3  f4  f5  f6  f7  f8  f9  f10  ...  f141  f142  f143  f144  \
id                                                ...                           
2335465   6  11  16  16  16  16  16  16  16   16  ...     1     1     0     0   
390270   15  11   0  16  16  16   0   0   0    0  ...     0     0     0     0   

         f145  f146  f147  f148  f149  f150  
id                                           
2335465     0     0     0     0     0     0  
390270      0     0     0     0     0     0  

[2 rows x 150 columns]

In [385]:
# посмотрим на структуру данных в y_train_balanced
y_train_balanced.head(2)

id
2335465    1
390270     1
Name: flag, dtype: int64

In [386]:
# проверим что выборки действительно совпадают по id
X_train_balanced.index.to_list() == y_train_balanced.index.to_list()

True

##### <span style="color:MediumSlateBlue">Baseline обучение модели Hist Gradient Boosting Classifier</span>

In [387]:
# обучаем модель Gradient Boosting Classifier
gradient_boosting = HistGradientBoostingClassifier(random_state=42)
gradient_boosting.fit(np.array(X_train_balanced)[:,list_n_last_features],np.array(y_train_balanced))

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_rf__pred_proba = gradient_boosting.predict_proba(X_train[:,list_n_last_features])[:,1]
y_valid_rf_pred_proba = gradient_boosting.predict_proba(X_valid[:,list_n_last_features])[:,1]

# Делаем предсказание для валидационной выборки
y_valid_rf_pred = gradient_boosting.predict(X_valid[:,list_n_last_features])

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_rf__pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_rf_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_rf_pred))

# time: 

ROC AUC на обучающем наборе 0.669
ROC AUC на валидационном наборе 0.657
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.98      0.61      0.75     68747
           1       0.06      0.62      0.10      2503

    accuracy                           0.61     71250
   macro avg       0.52      0.62      0.43     71250
weighted avg       0.95      0.61      0.73     71250



##### <span style="color:MediumSlateBlue">Подбор гиперпараметров модели</span>

In [1581]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'relative'
count_features = dict_spaces[feature_space]

# настроим оптимизацию гипер параметров
def optuna_hgbc(trial):
  # задаем пространства поиска гиперпараметров
  learning_rate = trial.suggest_float('learning_rate',0.2,0.6)
  max_iter = trial.suggest_int('max_iter', 50, 300,step = 1)
  max_leaf_nodes = trial.suggest_int('max_leaf_nodes', 2, 50,step = 1)
  max_depth = trial.suggest_int('max_depth', 1, 15,step = 1)
  min_samples_leaf = trial.suggest_int('min_samples_leaf', 1, 50,step = 1)
  max_features = trial.suggest_float('max_features',0.1,1)
  l2_regularization = trial.suggest_float('l2_regularization',0.01,1)
  class_0_weight = trial.suggest_float('class_0_weight',0.01,1)
  class_1_weight = trial.suggest_float('class_1_weight',0.01,1)
  n_last = trial.suggest_int('n_last', 5, 25,step = 1)
  class_1_percent = trial.suggest_float('class_1_percent',0.01,1)
  random_state = trial.suggest_int('random_state', 1, 1000000)


  # создаем модель
  optuna_gradient_boosting = HistGradientBoostingClassifier(
      learning_rate= learning_rate,
      max_iter = max_iter,
      max_leaf_nodes =max_leaf_nodes,
      max_depth = max_depth,
      min_samples_leaf = min_samples_leaf,
      max_features=max_features,
      l2_regularization = l2_regularization,
      class_weight={0:class_0_weight,1:class_1_weight},
      random_state=42)

  # с помощью функции features_from_transform_data_torow извлечем  
  # из данных transform_data_torow
  # признаки сооствествующие n_last последним клиенским операциям
  list_n_last_features = features_from_transform_data_torow(n_last,count_features,25)

  # загружаем обучующие наборы
  X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
  y_train_pd = pd.read_csv('target/target_train.csv')

  # поготовим данные y_train_pd к работе с функцией class_1_percent_samples
  y_train_pd.set_index('id',drop=False,inplace=True)

  # подготовим данные для обучения модели
  # с помощью функции class_1_percent_samples зададим долю класса 1
  list_c1_percent_id = class_1_percent_samples(y_train_pd,class_1_percent,random_state=random_state)[:1000000]

  # сформируем данные для обучения модели
  X_train_balanced = np.array(X_train_pd.loc[list_c1_percent_id])[:,list_n_last_features]
  y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

  # освободим память от "тяжелых" и ненужных файлов
  del X_train_pd, y_train_pd
  gc.collect()

  # я не воспользовался параметром timeout метода optimize потому, что  
  # optimize отставливает поиск параметров, если время обучения 
  # превышает timeout. Мне нужно чтобы поиск параметров продолжился.
  try:
    # для модуля func_time_out упакуем обучение модели в функцию try_func
    def try_func():
            return optuna_gradient_boosting.fit(X_train_balanced,y_train_balanced)
    # обучаем модель с ограничением по времени 10 минут (600 секунд)
    optuna_gradient_boosting = func_timeout.func_timeout(600, try_func)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train_balanced, y_train_balanced
    gc.collect()

    # подгружаем данные для тестирования
    X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()[:,list_n_last_features]
    y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
    X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()[:,list_n_last_features]
    y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

    # делаем предсказание на обучающем и валидационном наборе и считаем метрики
    roc_train = metrics.roc_auc_score(y_train, optuna_gradient_boosting.predict_proba(X_train)[:,1])
    roc_valid = metrics.roc_auc_score(y_valid, optuna_gradient_boosting.predict_proba(X_valid)[:,1])
    f1_score = metrics.f1_score(y_valid, optuna_gradient_boosting.predict(X_valid))
    recall_1 = metrics.recall_score(y_valid, optuna_gradient_boosting.predict(X_valid),average=None,zero_division=0)[1]
    precision_1 = metrics.precision_score(y_valid, optuna_gradient_boosting.predict(X_valid),average=None,zero_division=0)[1]

    # удаляем крупные файлы чтобы высвободить память 
    del X_train, X_valid, y_train, y_valid 
    gc.collect()

  except func_timeout.FunctionTimedOut:
    # освободим память от "тяжелых" и ненужных файлов
    del X_train_balanced, y_train_balanced
    gc.collect()

    # обьявим метрики пустыми значениями
    roc_train = 0
    roc_valid = 0
    f1_score = 0
    recall_1 = 0
    precision_1 = 0
    pass

  return roc_train, roc_valid, f1_score, recall_1, precision_1

In [1582]:
# cоздаем объект исследования
# чтобы модель не переобучалась минимизируем roc_train 
# и максимизируем roc_valid
optuna_study_hsbs = optuna.create_study(study_name='HistGradientBoostingClassifier_'+feature_space+'_torow', 
                               directions=['maximize','maximize','maximize','maximize','maximize'], 
                               sampler=optuna.samplers.TPESampler(),
                               pruner='Hyperband',
                               storage='sqlite:///optuna_studies.db',
                               load_if_exists=True)

# ну случай удаления обучения
# optuna.delete_study(study_name='HistGradientBoostingClassifier_'+feature_space+'_torow', storage='sqlite:///optuna_studies.db')

[I 2025-04-19 14:14:49,536] Using an existing study with name 'HistGradientBoostingClassifier_relative_torow' instead of creating a new one.


In [390]:
# ищем лучшую комбинацию гиперпараметров n_trials раз
optuna_study_hsbs.optimize(optuna_hgbc, n_trials=300)

[I 2025-04-17 14:32:41,240] Trial 0 finished with values: [0.6591413458267431, 0.6507050747504814, 0.11813842482100238, 0.27686775868957253, 0.07508939213349225] and parameters: {'learning_rate': 0.5657544112613853, 'max_iter': 204, 'max_leaf_nodes': 47, 'max_depth': 4, 'min_samples_leaf': 19, 'max_features': 0.5733047233115559, 'l2_regularization': 0.8525909715539403, 'class_0_weight': 0.5641428546995083, 'class_1_weight': 0.3153080040212603, 'n_last': 22, 'class_1_percent': 0.5284017867281716, 'random_state': 509015}.
[I 2025-04-17 14:32:44,275] Trial 1 finished with values: [0.5991992157667412, 0.5950933414064613, 0.06787704573497308, 1.0, 0.035130810689422864] and parameters: {'learning_rate': 0.29789515989667603, 'max_iter': 168, 'max_leaf_nodes': 47, 'max_depth': 12, 'min_samples_leaf': 42, 'max_features': 0.49630272027743566, 'l2_regularization': 0.27409122294349453, 'class_0_weight': 0.3470692192202094, 'class_1_weight': 0.4345523905626191, 'n_last': 9, 'class_1_percent': 0.968

In [1583]:
# из полученного результат соврмируем Data Frame
optuna_study_hsbs_pd = optuna_study_hsbs.trials_dataframe()
# переименуем столбы
optuna_study_hsbs_pd.rename(columns={
    'values_0': 'roc_train',
    'values_1': 'roc_valid',
    'values_2': 'f1_score',
    'values_3': 'recall_1',
    'values_4': 'precision_1'
},inplace=True)
# Выделим время потраченное на обучение модели
last_trail = optuna_study_hsbs_pd['number'].max()
optuna_study_hsbs_pd.tail(5)


number  roc_train  roc_valid  f1_score  recall_1  precision_1  \
295     295   0.679553   0.660607  0.077295  0.909309     0.040363   
296     296   0.644764   0.633353  0.067875  1.000000     0.035130   
297     297   0.697882   0.658170  0.122396  0.300439     0.076852   
298     298   0.685697   0.664083  0.109305  0.126249     0.096371   
299     299   0.674416   0.656237  0.068153  0.996005     0.035284   

                datetime_start          datetime_complete  \
295 2025-04-17 15:02:36.225169 2025-04-17 15:02:45.964150   
296 2025-04-17 15:02:45.969801 2025-04-17 15:02:53.574025   
297 2025-04-17 15:02:53.580990 2025-04-17 15:03:02.767211   
298 2025-04-17 15:03:02.772388 2025-04-17 15:03:11.413556   
299 2025-04-17 15:03:11.419314 2025-04-17 15:03:19.578299   

                  duration  params_class_0_weight  ...  \
295 0 days 00:00:09.738981               0.074705  ...   
296 0 days 00:00:07.604224               0.171301  ...   
297 0 days 00:00:09.186221               0.109978  ...   
298 0 days 00:00:08.641168               0.160042  ...   
299 0 days 00:00:08.158985               0.085721  ...   

     params_l2_regularization  params_learning_rate  params_max_depth  \
295                  0.222334              0.234179                 4   
296                  0.173813              0.224081                15   
297                  0.267503              0.277662                 8   
298                  0.143305              0.259717                 6   
299                  0.188231              0.330885                 5   

     params_max_features  params_max_iter  params_max_leaf_nodes  \
295             0.779626              157                     49   
296             0.741424              268                     28   
297             0.695588              113                     48   
298             0.718251               83                     50   
299             0.769814              262                     44   

     params_min_samples_leaf  params_n_last  params_random_state     state  
295                       29             25               226544  COMPLETE  
296                       45             18               997521  COMPLETE  
297                       36             16               614070  COMPLETE  
298                       31             22               689473  COMPLETE  
299                       37             24               515623  COMPLETE  

[5 rows x 22 columns]

In [1584]:
# покаждем статистику обучения
print('Максимальное значение метрики ROC AUC на валидационном наборе:',round(optuna_study_hsbs_pd['roc_valid'].max(),3))
print('Среднее значение метрики ROC AUC на валидационном наборе:',round(optuna_study_hsbs_pd['roc_valid'].mean(),3))
print('Максимальное значение метрики f1_score на валидационном наборе:',round(optuna_study_hsbs_pd['f1_score'].max(),3))
print('Среднее значение метрики f1_score на валидационном наборе:',round(optuna_study_hsbs_pd['f1_score'].mean(),3))
print('Максимальное значение метрики recall_1 на валидационном наборе:',round(optuna_study_hsbs_pd['recall_1'].max(),3))
print('Среднее значение метрики recall_1 на валидационном наборе:',round(optuna_study_hsbs_pd['recall_1'].mean(),3))
print('Максимальное значение метрики precision_1 на валидационном наборе:',round(optuna_study_hsbs_pd['precision_1'].max(),3))
print('Среднее значение метрики precision_1 на валидационном наборе:',round(optuna_study_hsbs_pd['precision_1'].mean(),3))

Максимальное значение метрики ROC AUC на валидационном наборе: 0.669
Среднее значение метрики ROC AUC на валидационном наборе: 0.656
Максимальное значение метрики f1_score на валидационном наборе: 0.127
Среднее значение метрики f1_score на валидационном наборе: 0.08
Максимальное значение метрики recall_1 на валидационном наборе: 1.0
Среднее значение метрики recall_1 на валидационном наборе: 0.46
Максимальное значение метрики precision_1 на валидационном наборе: 1.0
Среднее значение метрики precision_1 на валидационном наборе: 0.089


In [1599]:
# Построим зависимость метрик качества модели от number

fig = px.scatter(
    data_frame=optuna_study_hsbs_pd[(optuna_study_hsbs_pd['roc_valid']>0.99*optuna_study_hsbs_pd['roc_valid'].max())&
                                    (optuna_study_hsbs_pd['f1_score']>0.99*optuna_study_hsbs_pd['f1_score'].max())],
    x='number', #ось абсцисс
    y=['roc_train','roc_valid','recall_1','precision_1','f1_score'], #ось ординат
)
fig.update_layout(
    title ={
        'text':'Зависимость precision от гиперпараметров модели', # Имя рабочей плоскости
        'font':{'size':35,'family':"Times New Roman"}, # размер и стиль написания имени рабочей плоскости
        'x':0.5, # Смешение имени по оси "x" на половину рабочей плоскости
        },
    height =800,# Высота рабочей плоскости
    width = 1350, # Ширина рабочей плоскости
    bargap=0.2, # Добавил расстояния между столбами гистограммы
    xaxis_title='Величина метрики precision_1',
    yaxis_title='Величина параметра')
fig.update_xaxes(showspikes=True)
fig.update_yaxes(showspikes=True)

fig.show()

<span style="color:Blue">

Вывод:  

Их всех выбираем точку $number =231$.   
В этой точке оптимальные значения метрик $recall_1$ и $precision_1$, а  
также относительно высокая метрика $ROC AUC$.   
Посмотрим каким значениям гиперпараметров соотвествует выбранная точка.

In [1600]:
# определим номер лучшге варианта
best_optuna_number = 231

# сформируем словарь лучших гипирпарметров RandomForestClassifier
best_param_rf = {
    'learning_rate' : optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_learning_rate'].iloc[0],
    'max_iter' : optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_max_iter'].iloc[0],
    'max_leaf_nodes' : optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_max_leaf_nodes'].iloc[0],
    'max_depth' : optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_max_depth'].iloc[0],
    'min_samples_leaf' : optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_min_samples_leaf'].iloc[0],
    'max_features' : optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_max_features'].iloc[0],
    'l2_regularization' : optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_l2_regularization'].iloc[0],
    'class_weight' : {0: optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_class_0_weight'].iloc[0],
                      1: optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_class_1_weight'].iloc[0],}
    }

# определим перменные для лучших значений параметров
best_n_last = optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_n_last'].iloc[0]
best_class_1_percent = optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_class_1_percent'].iloc[0]
best_random_state = optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_random_state'].iloc[0]


# Выведем принятые наилучшие праметры
print('best learning rate:',round(best_param_rf['learning_rate'],3))
print('best max iter:',best_param_rf['max_iter'])
print('best max leaf nodes:',best_param_rf['max_leaf_nodes'])
print('best max depth:',best_param_rf['max_depth'])
print('best min samples leaf:',best_param_rf['min_samples_leaf'])
print('best max features:',round(best_param_rf['max_features'],3))
print('best l2 regularization:',round(best_param_rf['l2_regularization'],3))
print('best class 0 weight:',round(best_param_rf['class_weight'][0],3))
print('best class 1 weight:',round(best_param_rf['class_weight'][1],3))

print('best class 1 percent:',round(best_class_1_percent,3))
print('best n last:',best_n_last)
print('best random state:',best_random_state)
print('time for best train:',round(optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['duration'].iloc[0].seconds/60),'minutes')

print()
print('ROC AUC на обучающем наборе:', round(optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['roc_train'].iloc[0],3))
print('ROC AUC на валидационном наборе:', round(optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['roc_valid'].iloc[0],3))
print('precision класса 1:', round(optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['precision_1'].iloc[0],3))
print('recall класса 1:', round(optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['recall_1'].iloc[0],3))

best learning rate: 0.207
best max iter: 127
best max leaf nodes: 48
best max depth: 5
best min samples leaf: 49
best max features: 0.71
best l2 regularization: 0.06
best class 0 weight: 0.217
best class 1 weight: 0.547
best class 1 percent: 0.19
best n last: 24
best random state: 623704
time for best train: 0 minutes

ROC AUC на обучающем наборе: 0.682
ROC AUC на валидационном наборе: 0.666
precision класса 1: 0.084
recall класса 1: 0.249


##### <span style="color:MediumSlateBlue">Обучение модели с лучшими параметрами</span>

In [1601]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'relative'
count_features = dict_spaces[feature_space]

# с помощью функции features_from_transform_data_torow извлечем  
# из данных transform_data_torow
# признаки сооствествующие n_last последним клиенским операциям
list_n_last_features = features_from_transform_data_torow(best_n_last,count_features,25)

# загружаем обучующие наборы
X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)

# подготовим данные для обучения модели
# с помощью функции class_1_percent_samples зададим долю класса 1
list_c1_percent_id = class_1_percent_samples(y_train_pd,best_class_1_percent,random_state=best_random_state)[:1000000]

# сформируем данные для обучения модели
X_train_balanced = np.array(X_train_pd.loc[list_c1_percent_id])[:,list_n_last_features]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

# освободим память от "тяжелых" и ненужных файлов
del X_train_pd, y_train_pd
gc.collect()


# обучаем модель HistGradientBoostingClassifier с наилучшеми параметрами
gradient_boosting = HistGradientBoostingClassifier(
        **best_param_rf,
        random_state=42)
gradient_boosting.fit(X_train_balanced,y_train_balanced)

# освободим память от "тяжелых" и ненужных файлов
del X_train_balanced, y_train_balanced
gc.collect()

# подгружаем данные для тестирования
X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()[:,list_n_last_features]
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()[:,list_n_last_features]
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_gb__pred_proba = gradient_boosting.predict_proba(X_train)[:,1]
y_valid_gb_pred_proba = gradient_boosting.predict_proba(X_valid)[:,1]

# Делаем предсказание для валидационной выборки
y_valid_gb_pred = gradient_boosting.predict(X_valid)

# освободим память от "тяжелых" и ненужных файлов
del X_train, X_valid
gc.collect()

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_gb__pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_gb_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_gb_pred,zero_division=0))

# time: 2m 30s

ROC AUC на обучающем наборе 0.682
ROC AUC на валидационном наборе 0.666
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.97      0.90      0.93     68747
           1       0.08      0.25      0.13      2503

    accuracy                           0.88     71250
   macro avg       0.53      0.58      0.53     71250
weighted avg       0.94      0.88      0.91     71250



### <span style="color:RoyalBlue">Построение модели на сбалансированных данных подпространства payments torow</span>

#### <span style="color:MediumBlue">Построение модели Logistic Regression</span>

##### <span style="color:MediumSlateBlue">Формирование данных для обучения</span>

Анализ исходных данных, в частности target, показал что представленные данные   
имееют перекос: 96% клиентов у которых не случился дефолт (flag = 0),    
против 4 % - для которых произошел дефолт (flag = 1).  
С помощью функции class_1_percent_samples, сформируем сбаланисрованную выборку  
для обучения моделей.
За основу сбалансировных данных возьмем данные клиентов с дефолтом  
и к ним будем добирать необходимое количество клиентов до сбалансированности. 


Функция class_1_percent_samples принемает две переменные:
- target_data - массив с id и целевой переменной
- class_1_percent - процент класса 1 в результирующем массиве

In [409]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'service'
count_features = dict_spaces[feature_space]

In [410]:
# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

In [411]:
# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)
y_train_pd.head(4)

id  flag
id                    
1825800  1825800     0
2166483  2166483     0
2534345  2534345     0
1803283  1803283     0

In [412]:
# взглянем на сблансиорованность данных в y_train
y_train_pd['flag'].value_counts(normalize=True)

flag
0    0.964242
1    0.035758
Name: proportion, dtype: float64

In [413]:
# сбалансируем данные в y_train_pd
list_c1_percent_id = class_1_percent_samples(y_train_pd,0.5)
# list_c1_percent_features - список 'id' из y_train_pd соотвествующих  
# заданному проценту класса 1
len(list_c1_percent_id)

45860

In [414]:
# проверим сбалансированность полученного y_train
y_train_pd.loc[list_c1_percent_id]['flag'].value_counts(normalize=True)

flag
1    0.5
0    0.5
Name: proportion, dtype: float64

*transform_data_torow*, показываеются последние N операций клиента.  
В данных в *date_torow*, собраны последние 25 операций клиентов.

Предварительный анализ показывает, что медиальное значение количества клиентских  
операций равно 7. Поэтому, для начала, будем показывать моделе $n_{last} = 7$   
последних клиентских операций.

Для извлечения из *transform_data_torow_25* необходимого количества последних клиенских  
операций ($n_{last}$) используем функцию features_from_transform_data_torow.

Функция features_from_transform_data_torow примает следующие аргументы:
- $n_{last} = 7$ - необходимое количество последних клиентских операций; 
- $n_{groups} = 8$ - количество признаков в $date$ $features$;
- $N_{last} = 25$ - количество $n_{last}$ операций, показанных в transform_data_torow_25


In [415]:
# с помощью функции features_from_transform_data_torow извлечем  
# из данных transform_data_torow_25
# признаки сооствествующие 7 последним клиенским операциям
list_n_last_features = features_from_transform_data_torow(7,count_features,25)

In [416]:
# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']
# сформируем данные для проверики модели
X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

In [417]:
# посмотрим на структуру данных в X_train_balanced
X_train_balanced.head(2)

f1  f2  f3  f4  f5  f6  f7  f8  f9  f10  ...  f91  f92  f93  f94  \
id                                                ...                       
2335465   1   1   1   1   1   1   1   1   1    1  ...    1    1    0    0   
390270    1   1   1   1   1   1   0   0   0    0  ...    0    0    0    0   

         f95  f96  f97  f98  f99  f100  
id                                      
2335465    0    0    0    0    0     0  
390270     0    0    0    0    0     0  

[2 rows x 100 columns]

In [418]:
# посмотрим на структуру данных в y_train_balanced
y_train_balanced.head(2)

id
2335465    1
390270     1
Name: flag, dtype: int64

In [419]:
# проверим что выборки действительно совпадают по id
X_train_balanced.index.to_list() == y_train_balanced.index.to_list()

True

##### <span style="color:MediumSlateBlue">Baseline обучение модели LogisticRegression</span>

In [420]:
# обучаем модель логистической регрессии
logistic_regression = linear_model.LogisticRegression(random_state=42, max_iter=10000)
logistic_regression.fit(np.array(X_train_balanced)[:,list_n_last_features],np.array(y_train_balanced))

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_LR_pred_proba = logistic_regression.predict_proba(X_train[:,list_n_last_features])[:,1]
y_valid_LR_pred_proba = logistic_regression.predict_proba(X_valid[:,list_n_last_features])[:,1]

# Делаем предсказание для валидационной выборки
y_valid_LR_pred = logistic_regression.predict(X_valid[:,list_n_last_features])

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_LR_pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_LR_pred_proba),3))

print('Основные метрики на тестовом наборе:')
print(metrics.classification_report(y_valid,y_valid_LR_pred))

# time: 1m 12s

ROC AUC на обучающем наборе 0.592
ROC AUC на валидационном наборе 0.596
Основные метрики на тестовом наборе:
              precision    recall  f1-score   support

           0       0.97      0.55      0.70     68747
           1       0.05      0.60      0.09      2503

    accuracy                           0.55     71250
   macro avg       0.51      0.57      0.39     71250
weighted avg       0.94      0.55      0.68     71250



##### <span style="color:MediumSlateBlue">Анализ влияния scaler преобразования на качество и скорость схождения модели</span>

In [421]:
# формируем список из необходимых scaler
scalers = [MinMaxScaler(),RobustScaler() ,StandardScaler()]

# сформируем списко для заполнения данными результатов анализа
scalers_data = []

# установим ограничение на время обучения модели в 600 секунд (10 минут)
time_out = 600

for scaler in scalers:
        # для того чтобы следить за выполнением цикла введем индикатор
        print('current scaler: ', scaler)

         # сформируем список для заполнения данными текушего scaler
        current_scaler_data = [scaler]
        
        # выполним scaler преобразование
        X_train_s_balanced = scaler.fit_transform(np.array(X_train_balanced)[:,list_n_last_features])
        X_train_s = scaler.transform(X_train[:,list_n_last_features])
        X_valid_s = scaler.transform(X_valid[:,list_n_last_features])

        try:
                # для модуля func_time_out упакуем обучение модели в функцию try_func
                def try_func():
                        logistic_regression = linear_model.LogisticRegression(random_state=42, max_iter=10000)
                        return logistic_regression.fit(X_train_s_balanced,y_train_balanced)
                    
                # фиксируем время начала
                start_time = time.time()
                
                # запускаем обучение модели с ограничением по времени
                logistic_regression = func_timeout.func_timeout(time_out, try_func)
                
                # фиксируем время окончания обучения
                end_time = time.time()
                
                # запишем время обучения модели
                current_scaler_data.append(round(end_time-start_time))

                # Делаем предсказание для обучающей и валидационной выборки
                y_valid_lr_pred = logistic_regression.predict(X_valid_s)
                
                # для метрик ROC AUC делаем предсказание модели для обучающей и валидационной выборки  
                # в виде вероятности принадлежности к классу 1 
                y_train_lr_pred_proba = logistic_regression.predict_proba(X_train_s)[:,1]
                y_valid_lr_pred_proba = logistic_regression.predict_proba(X_valid_s)[:,1]

                #Считаем метрики ROC AUC yна обуающем и валидационном наборе и добавляем их в спискок
                current_scaler_data.append(round(metrics.roc_auc_score(y_train, y_train_lr_pred_proba),3))
                current_scaler_data.append(round(metrics.roc_auc_score(y_valid, y_valid_lr_pred_proba),3))

                #Считаем метрики для класса 0 на валидационном наборе и добавляем их в список
                current_scaler_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))
                current_scaler_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))


                #Считаем метрики для класса 1 на валидационном набопе и добавляем их в список
                current_scaler_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))
                current_scaler_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))

                # добавляем полученные данные в список scalers_data
                scalers_data.append(current_scaler_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                scaler_pd =pd.DataFrame(
                        columns=['scaler','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = scalers_data)
                # сохраняем dataframe
                scaler_pd.to_csv('data_recovery/scaler_pd.csv',index=False)
               
                # очистим output от прошедшей итерации
                clear_output()

        except func_timeout.FunctionTimedOut:
                # если время обучения привышает лимит
                # запишем в current_scaler_data соотвествующую данные
                current_scaler_data = [scaler,'>30m',0,0,0,0,0,0]
                # добавляем полученные данные в список scalers_data
                scalers_data.append(current_scaler_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                scaler_pd =pd.DataFrame(
                        columns=['scaler','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = scalers_data)
                # сохраняем dataframe
                scaler_pd.to_csv('data_recovery/scaler_pd.csv',index=False)
                
                # очистим output от прошедшей итерации
                clear_output()
                # переходим к следующему scaler
                pass
# очистим output
clear_output()

# сформируем данные соотвествующие лучщему ROC AUC на валидацинном наборе
best_roc_valid_data = scaler_pd[scaler_pd['roc_valid']==scaler_pd['roc_valid'].max()]

# выведем лучший результат на валидационном наборе
print('result:')
print('best scaler on valid:',best_roc_valid_data.iloc[0]['scaler'])
print('ROC AUC on train:', best_roc_valid_data.iloc[0]['roc_train'])
print('ROC AUC on valid:', best_roc_valid_data.iloc[0]['roc_valid'])
print('Time fit for best scaler:', best_roc_valid_data.iloc[0]['time_fit'],' seconds')

# выведем полученный dataframe
scaler_pd

# time: 

result:
best scaler on valid: MinMaxScaler()
ROC AUC on train: 0.593
ROC AUC on valid: 0.596
Time fit for best scaler: 0  seconds


scaler  time_fit  roc_train  roc_valid  recall_0  precision_0  \
0    MinMaxScaler()         0      0.593      0.596     0.547        0.974   
1    RobustScaler()         0      0.593      0.596     0.546        0.974   
2  StandardScaler()         0      0.593      0.596     0.547        0.974   

   recall_1  precision_1  
0     0.599        0.046  
1     0.597        0.046  
2     0.595        0.046

##### <span style="color:MediumSlateBlue"> Анализ влияния solver оптимизатора на качество и скорость обучения модели</span>

Проверим качество и скорость сходимости модели при разных solver  
Проверку осуществим через цикл  
Чтобы модель не сходилась бесконечно с помощью модуля func_timeout  
поставим ограничение времени схождения в 10 минут

In [422]:
# подготовим данные для обучения модели

# обьявим scaler
scaler = StandardScaler()
# выполним scaler преобразование
X_train_s_balanced = scaler.fit_transform(np.array(X_train_balanced)[:,list_n_last_features])
X_train_s = scaler.transform(X_train[:,list_n_last_features])
X_valid_s = scaler.transform(X_valid[:,list_n_last_features])

# time: 10s

In [423]:
# Зададим список solvers
solvers_list = ['lbfgs', 'liblinear', 'newton-cg', 'newton-cholesky', 'sag', 'saga']

# сформируем список для заполнения
solvers_data = []

# установим ограничение на время обучения модели в 300 секунд (5 минут)
time_out = 300

for solver in solvers_list:
        # для того чтобы следить за выполнением цикла введем индикатор
        print('current solver: ', solver)

         # сформируем список для заполнения данными текушего solver
        current_solver_data = [solver]
        
        try:
                # для модуля func_time_out упакуем обучение модели в функцию try_func
                def try_func():
                        logistic_regression = linear_model.LogisticRegression(solver= solver,
                                                                  random_state=42, 
                                                                  max_iter=10000)
                        return logistic_regression.fit(X_train_s_balanced,y_train_balanced)
                    
                # фиксируем время начала
                start_time = time.time()
                
                # запускаем обучение модели с ограничением по времени
                logistic_regression = func_timeout.func_timeout(time_out, try_func)
                
                # фиксируем время окончания обучения
                end_time = time.time()
                
                # запишем время обучения модели
                current_solver_data.append(round(end_time-start_time))

                # Делаем предсказание для обучающей и валидационной выборки
                y_valid_lr_pred = logistic_regression.predict(X_valid_s)
                
                # для метрик ROC AUC делаем предсказание модели для обучающей и валидационной выборки  
                # в виде вероятности принадлежности к классу 1 
                y_train_lr_pred_proba = logistic_regression.predict_proba(X_train_s)[:,1]
                y_valid_lr_pred_proba = logistic_regression.predict_proba(X_valid_s)[:,1]

                #Считаем метрики ROC AUC yна обуающем и валидационном наборе и добавляем их в спискок
                current_solver_data.append(round(metrics.roc_auc_score(y_train, y_train_lr_pred_proba),3))
                current_solver_data.append(round(metrics.roc_auc_score(y_valid, y_valid_lr_pred_proba),3))

                #Считаем метрики для класса 0 на валидационном наборе и добавляем их в список
                current_solver_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))
                current_solver_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))


                #Считаем метрики для класса 1 на валидационном набопе и добавляем их в список
                current_solver_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))
                current_solver_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))

                # запишем данные полученные на одной итерации
                solvers_data.append(current_solver_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                solvers_pd =pd.DataFrame(
                        columns=['solver','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = solvers_data)
                # сохраняем dataframe
                solvers_pd.to_csv('data_recovery/solvers_pd.csv',index=False)
               
                # очистим output от прошедшей итерации
                clear_output()

        except func_timeout.FunctionTimedOut:
                # если время обучения привышает лимит
                # запишем в current_solver_data соотвествующую данные
                current_solver_data = [solver,'>10m',0,0,0,0,0,0]
                # добавляем полученные данные в список solvers_data
                solvers_data.append(current_solver_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                solvers_pd =pd.DataFrame(
                        columns=['solver','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = solvers_data)
                # сохраняем dataframe
                solvers_pd.to_csv('data_recovery/solvers_pd.csv',index=False)
                
                # очистим output от прошедшей итерации
                clear_output()
                # переходим к следующему solver
                pass
# очистим output
clear_output()

# сформируем данные соотвествующие лучщему ROC AUC на валидацинном наборе
best_roc_valid_data = solvers_pd[solvers_pd['roc_valid']==solvers_pd['roc_valid'].max()]

# выведем лучший результат на валидационном наборе
print('result:')
print('best solver on valid:',best_roc_valid_data.iloc[0]['solver'])
print('ROC AUC on train:', best_roc_valid_data.iloc[0]['roc_train'])
print('ROC AUC on valid:', best_roc_valid_data.iloc[0]['roc_valid'])
print('Time fit for best solver:', best_roc_valid_data.iloc[0]['time_fit'],' seconds')

# выведем полученный dataframe
solvers_pd

# time: 11m 35s

result:
best solver on valid: lbfgs
ROC AUC on train: 0.593
ROC AUC on valid: 0.596
Time fit for best solver: 0  seconds


solver  time_fit  roc_train  roc_valid  recall_0  precision_0  \
0            lbfgs         0      0.593      0.596     0.547        0.974   
1        liblinear         0      0.593      0.596     0.546        0.974   
2        newton-cg         0      0.593      0.596     0.546        0.974   
3  newton-cholesky         0      0.593      0.596     0.546        0.974   
4              sag         0      0.593      0.596     0.546        0.974   
5             saga         0      0.593      0.596     0.546        0.974   

   recall_1  precision_1  
0     0.595        0.046  
1     0.598        0.046  
2     0.596        0.046  
3     0.598        0.046  
4     0.598        0.046  
5     0.598        0.046

##### <span style="color:MediumSlateBlue">Подбор гиперпараметров модели</span>

In [1602]:
# для выбора sceler преобразвания на понадобится словарь
dict_scalers ={
    'MinMaxScaler':MinMaxScaler(),
    'RobustScaler':RobustScaler(),
    'StandardScaler':StandardScaler(),
}
# определим пространство признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'payments'
count_features = dict_spaces[feature_space]

# настроим оптимизацию гипер параметров
def optuna_lg(trial):
  # задаем пространства поиска гиперпараметров
  C = trial.suggest_float('C',0.01,1)
  solver = trial.suggest_categorical('solver', ['lbfgs', 'liblinear', 'newton-cg', 'newton-cholesky'])
  class_0_weight = trial.suggest_float('class_0_weight',0.01,1)
  class_1_weight = trial.suggest_float('class_1_weight',0.01,1)
  n_last = trial.suggest_int('n_last', 10, 25,step = 1)
  class_1_percent = trial.suggest_float('class_1_percent',0.01,1)
  scaler = trial.suggest_categorical('scaler', ['MinMaxScaler', 'RobustScaler','StandardScaler'])
  random_state = trial.suggest_int('random_state', 1, 1000000)

  # создаем модель
  optuna_log_reg = linear_model.LogisticRegression(
      solver=solver,
      C=C,
      class_weight={0:class_0_weight,1:class_1_weight},
      random_state=random_state,
      max_iter=10000)

  # с помощью функции features_from_transform_data_torow извлечем  
  # из данных transform_data_torow
  # признаки сооствествующие n_last последним клиенским операциям
  list_n_last_features = features_from_transform_data_torow(n_last,count_features,25)

  # обьявим scaler
  scaler = dict_scalers[scaler]

  # загружаем обучующие наборы
  X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
  y_train_pd = pd.read_csv('target/target_train.csv')

  # поготовим данные y_train_pd к работе с функцией class_1_percent_samples
  y_train_pd.set_index('id',drop=False,inplace=True)

  # подготовим данные для обучения модели
  # с помощью функции class_1_percent_samples зададим долю 
  # класса 1
  list_c1_percent_id = class_1_percent_samples(y_train_pd,class_1_percent,random_state=random_state)[:1000000]

  # сформируем данные для обучения базовой модели
  X_train_s_balanced = scaler.fit_transform(np.array(X_train_pd.loc[list_c1_percent_id])[:,list_n_last_features])
  y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

  # освободим память от "тяжелых" и ненужных файлов
  del X_train_pd, y_train_pd
  gc.collect()

  # я не воспользовался параметром timeout метода optimize потому, что  
  # optimize отставливает поиск параметров, если время обучения 
  # превышает timeout. Мне нужно чтобы поиск параметров продолжился.
  try:
    # для модуля func_time_out упакуем обучение модели в функцию try_func
    def try_func():
            return optuna_log_reg.fit(X_train_s_balanced, y_train_balanced)
    # обучаем модель с ограничением по времени 10 минут (600 секунд)
    optuna_log_reg = func_timeout.func_timeout(600, try_func)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train_s_balanced,y_train_balanced
    gc.collect()

    # подгружаем данные для тестирования
    X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()[:,list_n_last_features]
    y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
    X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()[:,list_n_last_features]
    y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

    # сформируем данные для проверки модели
    X_train_s = scaler.transform(X_train)
    X_valid_s = scaler.transform(X_valid)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train, X_valid
    gc.collect()

    # делаем предсказание на обучающем и валидационном наборе и считаем метрики
    roc_train = metrics.roc_auc_score(y_train, optuna_log_reg.predict_proba(X_train_s)[:,1])
    roc_valid = metrics.roc_auc_score(y_valid, optuna_log_reg.predict_proba(X_valid_s)[:,1])
    f1_score = metrics.f1_score(y_valid, optuna_log_reg.predict(X_valid_s))
    recall_1 = metrics.recall_score(y_valid, optuna_log_reg.predict(X_valid_s),average=None,zero_division=0)[1]
    precision_1 = metrics.precision_score(y_valid, optuna_log_reg.predict(X_valid_s),average=None,zero_division=0)[1]

    del X_train_s, X_valid_s, y_train, y_valid
    gc.collect()

  except func_timeout.FunctionTimedOut:
    # освободим память от "тяжелых" и ненужных файлов
    del X_train_s_balanced, y_train_balanced
    gc.collect()

    # обьявим метрики пустыми значениями
    roc_train = 0
    roc_valid = 0
    f1_score = 0
    recall_1 = 0
    precision_1 = 0
    pass

  return roc_train, roc_valid, f1_score, recall_1, precision_1

In [1603]:
# cоздаем объект исследования
# чтобы модель не переобучалась минимизируем roc_train 
# и максимизируем roc_valid
optuna_study_lg = optuna.create_study(study_name='LogisticRegression_'+feature_space+'_torow', 
                               directions=['maximize','maximize','maximize','maximize','maximize'], 
                               sampler=optuna.samplers.TPESampler(),
                               pruner='Hyperband',
                               storage='sqlite:///optuna_studies.db',
                               load_if_exists=True)
# на случай удаления 
# optuna.delete_study(study_name='LogisticRegression_'+feature_space+'_torow', storage='sqlite:///optuna_studies.db')

[I 2025-04-19 14:20:24,741] Using an existing study with name 'LogisticRegression_payments_torow' instead of creating a new one.


In [426]:
# ищем лучшую комбинацию гиперпараметров n_trials раз
optuna_study_lg.optimize(optuna_lg, n_trials=300)

[I 2025-04-17 15:04:01,415] Trial 0 finished with values: [0.6445749639570317, 0.6335478665510039, 0.0, 0.0, 0.0] and parameters: {'C': 0.6548081896408989, 'solver': 'newton-cholesky', 'class_0_weight': 0.948066939786244, 'class_1_weight': 0.43811740498629337, 'n_last': 11, 'class_1_percent': 0.1388596515144184, 'scaler': 'MinMaxScaler', 'random_state': 764451}.
[I 2025-04-17 15:04:15,110] Trial 1 finished with values: [0.6476430137820659, 0.6314662618975664, 0.02276064610866373, 0.012385137834598482, 0.14027149321266968] and parameters: {'C': 0.4029175472620048, 'solver': 'liblinear', 'class_0_weight': 0.7300797244429784, 'class_1_weight': 0.48575802606187873, 'n_last': 21, 'class_1_percent': 0.2151183757371583, 'scaler': 'RobustScaler', 'random_state': 543080}.
[I 2025-04-17 15:04:21,317] Trial 2 finished with values: [0.6405754075926344, 0.6320943995748893, 0.09590177534428405, 0.11546144626448263, 0.08200908059023837] and parameters: {'C': 0.1938045536055419, 'solver': 'liblinear',

In [1604]:
# из полученного результат соврмируем Data Frame
optuna_study_lg_pd = optuna_study_lg.trials_dataframe().dropna()
# переименуем столбы
optuna_study_lg_pd.rename(columns={
    'values_0': 'roc_train',
    'values_1': 'roc_valid',
    'values_2': 'f1_score',
    'values_3': 'recall_1',
    'values_4': 'precision_1'
},inplace=True)
# Выделим время потраченное на обучение модели
optuna_study_lg_pd.head(5)

number  roc_train  roc_valid  f1_score  recall_1  precision_1  \
0       0   0.644575   0.633548  0.000000  0.000000     0.000000   
1       1   0.647643   0.631466  0.022761  0.012385     0.140271   
2       2   0.640575   0.632094  0.095902  0.115461     0.082009   
3       3   0.647433   0.631645  0.007761  0.003995     0.135135   
4       4   0.625181   0.614364  0.068049  0.997603     0.035226   

              datetime_start          datetime_complete  \
0 2025-04-17 15:03:52.546617 2025-04-17 15:04:01.412749   
1 2025-04-17 15:04:01.419130 2025-04-17 15:04:15.107443   
2 2025-04-17 15:04:15.113458 2025-04-17 15:04:21.315545   
3 2025-04-17 15:04:21.321157 2025-04-17 15:04:36.216896   
4 2025-04-17 15:04:36.222559 2025-04-17 15:04:42.531957   

                duration  params_C  params_class_0_weight  \
0 0 days 00:00:08.866132  0.654808               0.948067   
1 0 days 00:00:13.688313  0.402918               0.730080   
2 0 days 00:00:06.202087  0.193805               0.788835   
3 0 days 00:00:14.895739  0.962263               0.809333   
4 0 days 00:00:06.309398  0.657313               0.920792   

   params_class_1_percent  params_class_1_weight  params_n_last  \
0                0.138860               0.438117             11   
1                0.215118               0.485758             21   
2                0.717330               0.146841             14   
3                0.166376               0.590491             19   
4                0.904635               0.515986             13   

   params_random_state params_scaler    params_solver     state  
0               764451  MinMaxScaler  newton-cholesky  COMPLETE  
1               543080  RobustScaler        liblinear  COMPLETE  
2               889659  MinMaxScaler        liblinear  COMPLETE  
3               606315  RobustScaler        liblinear  COMPLETE  
4               302019  RobustScaler        liblinear  COMPLETE

In [1605]:
# покаждем статистику обучения
print('Максимальное значение метрики ROC AUC на валидационном наборе:',round(optuna_study_lg_pd['roc_valid'].max(),3))
print('Среднее значение метрики ROC AUC на валидационном наборе:',round(optuna_study_lg_pd['roc_valid'].mean(),3))
print('Максимальное значение метрики f1_score на валидационном наборе:',round(optuna_study_lg_pd['f1_score'].max(),3))
print('Среднее значение метрики f1_score на валидационном наборе:',round(optuna_study_lg_pd['f1_score'].mean(),3))
print('Максимальное значение метрики recall_1 на валидационном наборе:',round(optuna_study_lg_pd['recall_1'].max(),3))
print('Среднее значение метрики recall_1 на валидационном наборе:',round(optuna_study_lg_pd['recall_1'].mean(),3))
print('Максимальное значение метрики precision_1 на валидационном наборе:',round(optuna_study_lg_pd['precision_1'].max(),3))
print('Среднее значение метрики precision_1 на валидационном наборе:',round(optuna_study_lg_pd['precision_1'].mean(),3))

Максимальное значение метрики ROC AUC на валидационном наборе: 0.637
Среднее значение метрики ROC AUC на валидационном наборе: 0.632
Максимальное значение метрики f1_score на валидационном наборе: 0.119
Среднее значение метрики f1_score на валидационном наборе: 0.078
Максимальное значение метрики recall_1 на валидационном наборе: 1.0
Среднее значение метрики recall_1 на валидационном наборе: 0.406
Максимальное значение метрики precision_1 на валидационном наборе: 1.0
Среднее значение метрики precision_1 на валидационном наборе: 0.078


In [1606]:
# Визуализируем метрики полученные при optuna оптимизации
fig = px.scatter(
    data_frame=optuna_study_lg_pd[(optuna_study_lg_pd['roc_valid']>0.99*optuna_study_lg_pd['roc_valid'].max())&
                                (optuna_study_lg_pd['f1_score']>0.99*optuna_study_lg_pd['f1_score'].max())],
    x='number', #ось абсцисс
    y=['roc_train','roc_valid','recall_1','precision_1','f1_score'], #ось ординат
)
fig.update_layout(
    title ={
        'text':'Зависимость качества модели от trials optuna', # Имя рабочей плоскости
        'font':{'size':35,'family':"Times New Roman"}, # размер и стиль написания имени рабочей плоскости
        'x':0.5, # Смешение имени по оси "x" на половину рабочей плоскости
        },
    height =800,# Высота рабочей плоскости
    width = 1350, # Ширина рабочей плоскости
    bargap=0.2, # Добавил расстояния между столбами гистограммы
    xaxis_title='trials optuna',
    yaxis_title='Величина метрики')
fig.update_xaxes(showspikes=True)
fig.update_yaxes(showspikes=True)

fig.show()

<span style="color:Blue">

Вывод:  

Их всех выбираем точку $number =229$.   
В этой точке одно из самых больших значений $ROC AUC$.  
Посмотрим каким значениям гиперпараметров соотвествует выбранная точка.

In [1608]:
# определим номер лучшге варианта
best_optuna_number = 229

# сформируем словарь лучших гипирпарметров RandomForestClassifier
best_param_lr_torow = {
    'C' : round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_C'].iloc[0],3),
    'class_weight' : {0:round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_class_0_weight'].iloc[0],3),
                      1:round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_class_1_weight'].iloc[0],3)},
    }
# создадим перменные
best_n_last = int(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_n_last'].iloc[0])
best_scaler = optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_scaler'].iloc[0]
best_class_1_percent = optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_class_1_percent'].iloc[0]
best_random_state = int(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_random_state'].iloc[0])
# Выведем принятые наилучшие праметры
print('best C:',best_param_lr_torow['C'])
print('best class 0 weight:',best_param_lr_torow['class_weight'][0])
print('best class 1 weight:',best_param_lr_torow['class_weight'][1])

print('best class 1 percent:',round(best_class_1_percent,3))
print('best scaler:',best_scaler)
print('best n_last:',round(best_n_last,3))
print('best best random state:',best_random_state)
print('time for best train:',round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['duration'].iloc[0].seconds/60),'minutes')

print()
print('ROC AUC на обучающем наборе:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['roc_train'].iloc[0],3))
print('ROC AUC на валидационном наборе:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['roc_valid'].iloc[0],3))
print('precision класса 1:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['precision_1'].iloc[0],3))
print('recall класса 1:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['recall_1'].iloc[0],3))

best C: 0.358
best class 0 weight: 0.585
best class 1 weight: 0.553
best class 1 percent: 0.392
best scaler: StandardScaler
best n_last: 10
best best random state: 601285
time for best train: 0 minutes

ROC AUC на обучающем наборе: 0.644
ROC AUC на валидационном наборе: 0.635
precision класса 1: 0.079
recall класса 1: 0.235


##### <span style="color:MediumSlateBlue">Обучение модели с лучшими параметрами</span>

In [436]:
# для выбора sceler преобразвания на понадобится словарь
dict_scalers ={
    'MinMaxScaler':MinMaxScaler(),
    'RobustScaler':RobustScaler(),
    'StandardScaler':StandardScaler(),
}

# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'payments'
count_features = dict_spaces[feature_space]

# с помощью функции features_from_transform_data_torow извлечем  
# из данных transform_data_torow_25
# признаки сооствествующие n_last последним клиенским операциям
list_n_last_features = features_from_transform_data_torow(best_n_last,count_features,25)

# обьявим scaler
scaler = dict_scalers[best_scaler]

# загружаем обучующие наборы
X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)

# подготовим данные для обучения модели
# с помощью функции class_1_percent_samples зададим долю 
# класса 1
list_c1_percent_id = class_1_percent_samples(y_train_pd,best_class_1_percent,random_state=best_random_state)[:1000000]

# сформируем данные для обучения базовой модели
X_train_s_balanced = scaler.fit_transform(np.array(X_train_pd.loc[list_c1_percent_id])[:,list_n_last_features])
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

# освободим память от "тяжелых" и ненужных файлов
del X_train_pd, y_train_pd
gc.collect()


# обучаем модель LogisticRegression с наилучшеми параметрами
logistic_regression = linear_model.LogisticRegression(
        **best_param_lr_torow,
        random_state=best_random_state,
        max_iter=10000)
logistic_regression.fit(X_train_s_balanced,y_train_balanced)

# удаляем крупные файлы чтобы высвободить память 
del X_train_s_balanced,y_train_balanced
gc.collect()

# подгружаем данные для тестирования
X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()[:,list_n_last_features]
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()[:,list_n_last_features]
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()
    
# сформируем данные для проверки модели
X_train_s = scaler.transform(X_train)
X_valid_s = scaler.transform(X_valid)

# удаляем крупные файлы чтобы высвободить память 
del X_train, X_valid
gc.collect()

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_lr_pred_proba = logistic_regression.predict_proba(X_train_s)[:,1]
y_valid_lr_pred_proba = logistic_regression.predict_proba(X_valid_s)[:,1]

# Делаем предсказание для валидационной выборки
y_valid_lr_pred = logistic_regression.predict(X_valid_s)

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_lr_pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_lr_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_lr_pred,zero_division=0))

# time: 2m 40s

ROC AUC на обучающем наборе 0.644
ROC AUC на валидационном наборе 0.635
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.97      0.98      0.97     68747
           1       0.10      0.05      0.07      2503

    accuracy                           0.95     71250
   macro avg       0.54      0.52      0.52     71250
weighted avg       0.94      0.95      0.94     71250



#### <span style="color:MediumBlue">Построение модели Random Forest Classifier</span>

##### <span style="color:MediumSlateBlue">Формирование данных для обучения</span>

Анализ исходных данных, в частности target, показал что представленные данные   
имееют перекос: 96% клиентов у которых не случился дефолт (flag = 0),    
против 4 % - для которых произошел дефолт (flag = 1).  
С помощью функции class_1_percent_samples, сформируем сбаланисрованную выборку  
для обучения моделей.
За основу сбалансировных данных возьмем данные клиентов с дефолтом  
и к ним будем добирать необходимое количество клиентов до сбалансированности. 


Функция class_1_percent_samples принемает две переменные:
- target_data - массив с id и целевой переменной
- class_1_percent - процент класса 1 в результирующем массиве

In [444]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'service'
count_features = dict_spaces[feature_space]

In [445]:
# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

In [446]:
# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)
y_train_pd.head(4)

id  flag
id                    
1825800  1825800     0
2166483  2166483     0
2534345  2534345     0
1803283  1803283     0

In [447]:
# взглянем на сблансиорованность данных в y_train
y_train_pd['flag'].value_counts(normalize=True)

flag
0    0.964242
1    0.035758
Name: proportion, dtype: float64

In [448]:
# сбалансируем данные в y_train_pd
list_c1_percent_id = class_1_percent_samples(y_train_pd,0.5)
# list_c1_percent_features - список 'id' из y_train_pd соотвествующих  
# заданному проценту класса 1
len(list_c1_percent_id)

45860

In [449]:
# проверим сбалансированность полученного y_train
y_train_pd.loc[list_c1_percent_id]['flag'].value_counts(normalize=True)

flag
1    0.5
0    0.5
Name: proportion, dtype: float64

*transform_data_torow*, показываеются последние N операций клиента.  
В данных в *date_torow*, собраны последние 25 операций клиентов.

Предварительный анализ показывает, что медиальное значение количества клиентских  
операций равно 7. Поэтому, для начала, будем показывать моделе $n_{last} = 7$   
последних клиентских операций.

Для извлечения из *transform_data_torow_25* необходимого количества последних клиенских  
операций ($n_{last}$) используем функцию features_from_transform_data_torow.

Функция features_from_transform_data_torow примает следующие аргументы:
- $n_{last} = 7$ - необходимое количество последних клиентских операций; 
- $n_{groups} = 8$ - количество признаков в $date$ $features$;
- $N_{last} = 25$ - количество $n_{last}$ операций, показанных в transform_data_torow_25


In [450]:
# с помощью функции features_from_transform_data_torow извлечем  
# из данных transform_data_torow_25
# признаки сооствествующие 7 последним клиенским операциям
list_n_last_features = features_from_transform_data_torow(7,count_features,25)

In [451]:
# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']
# сформируем данные для проверики модели
X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

In [452]:
# посмотрим на структуру данных в X_train_balanced
X_train_balanced.head(2)

f1  f2  f3  f4  f5  f6  f7  f8  f9  f10  ...  f91  f92  f93  f94  \
id                                                ...                       
2335465   1   1   1   1   1   1   1   1   1    1  ...    1    1    0    0   
390270    1   1   1   1   1   1   0   0   0    0  ...    0    0    0    0   

         f95  f96  f97  f98  f99  f100  
id                                      
2335465    0    0    0    0    0     0  
390270     0    0    0    0    0     0  

[2 rows x 100 columns]

In [453]:
# посмотрим на структуру данных в y_train_balanced
y_train_balanced.head(2)

id
2335465    1
390270     1
Name: flag, dtype: int64

In [454]:
# проверим что выборки действительно совпадают по id
X_train_balanced.index.to_list() == y_train_balanced.index.to_list()

True

##### <span style="color:MediumSlateBlue">Baseline обучение модели RandomForestClassifier</span>

In [455]:
# обучаем модель логистической регрессии
# чтобы модель пыталась найти связь во всех признаках
random_forest = RandomForestClassifier(random_state=42, n_jobs=-1)
random_forest.fit(np.array(X_train_balanced)[:,list_n_last_features],np.array(y_train_balanced))

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_rf__pred_proba = random_forest.predict_proba(X_train[:,list_n_last_features])[:,1]
y_valid_rf_pred_proba = random_forest.predict_proba(X_valid[:,list_n_last_features])[:,1]

# Делаем предсказание для валидационной выборки
y_valid_rf_pred = random_forest.predict(X_valid[:,list_n_last_features])

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_rf__pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_rf_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_rf_pred))

# time: 2m 5s

ROC AUC на обучающем наборе 0.783
ROC AUC на валидационном наборе 0.58
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.97      0.53      0.69     68747
           1       0.04      0.60      0.08      2503

    accuracy                           0.54     71250
   macro avg       0.51      0.57      0.39     71250
weighted avg       0.94      0.54      0.67     71250



##### <span style="color:MediumSlateBlue">Подбор гиперпараметров модели</span>

In [1609]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'payments'
count_features = dict_spaces[feature_space]

# настроим оптимизацию гипер параметров
def optuna_rf(trial):
  # задаем пространства поиска гиперпараметров
  # задаем пространства поиска гиперпараметров
  n_estimators = trial.suggest_int('n_estimators', 50, 150,step = 5)
  criterion = trial.suggest_categorical('criterion',['gini', 'entropy', 'log_loss'])
  max_depth = trial.suggest_int('max_depth', 9, 20,step = 1)
  min_samples_split = trial.suggest_int('min_samples_split', 5, 15,step = 1)
  min_samples_leaf = trial.suggest_int('min_samples_leaf', 5, 25,step = 1)
  max_features = trial.suggest_float('max_features',0.1,1)
  max_samples = trial.suggest_float('max_samples',0.1,1)
  class_0_weight = trial.suggest_float('class_0_weight',0.01,1)
  class_1_weight = trial.suggest_float('class_1_weight',0.01,1)
  n_last = trial.suggest_int('n_last', 5, 25,step = 1)
  class_1_percent = trial.suggest_float('class_1_percent',0.01,1)
  random_state = trial.suggest_int('random_state', 1, 1000000)


  # создаем модель
  optuna_random_forest = RandomForestClassifier(
      n_estimators = n_estimators, 
      criterion = criterion,
      max_depth = max_depth,
      min_samples_split = min_samples_split,  
      min_samples_leaf = min_samples_leaf,
      max_features=max_features,
      max_samples=max_samples,
      class_weight={0:class_0_weight,1:class_1_weight},
      n_jobs=-1,
      random_state=random_state)

  # с помощью функции features_from_transform_data_torow извлечем  
  # из данных transform_data_torow
  # признаки сооствествующие n_last последним клиенским операциям
  list_n_last_features = features_from_transform_data_torow(n_last,count_features,25)

  # загружаем обучующие наборы
  X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
  y_train_pd = pd.read_csv('target/target_train.csv')

  # поготовим данные y_train_pd к работе с функцией class_1_percent_samples
  y_train_pd.set_index('id',drop=False,inplace=True)

  # подготовим данные для обучения модели
  # с помощью функции class_1_percent_samples зададим долю 
  # класса 1
  list_c1_percent_id = class_1_percent_samples(y_train_pd,class_1_percent,random_state=random_state)[:1000000]

  # сформируем данные для обучения базовой модели
  X_train_balanced = np.array(X_train_pd.loc[list_c1_percent_id])[:,list_n_last_features]
  y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

  # освободим память от "тяжелых" и ненужных файлов
  del X_train_pd, y_train_pd
  gc.collect()

  # я не воспользовался параметром timeout метода optimize потому, что  
  # optimize отставливает поиск параметров, если время обучения 
  # превышает timeout. Мне нужно чтобы поиск параметров продолжился.
  try:
    # для модуля func_time_out упакуем обучение модели в функцию try_func
    def try_func():
            return optuna_random_forest.fit(X_train_balanced,y_train_balanced)
    # обучаем модель с ограничением по времени 10 минут (600 секунд)
    optuna_random_forest = func_timeout.func_timeout(600, try_func)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train_balanced, y_train_balanced
    gc.collect()

    # подгружаем данные для тестирования
    X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()[:,list_n_last_features]
    y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
    X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()[:,list_n_last_features]
    y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

    # делаем предсказание на обучающем и валидационном наборе и считаем метрики
    roc_train = metrics.roc_auc_score(y_train, optuna_random_forest.predict_proba(X_train)[:,1])
    roc_valid = metrics.roc_auc_score(y_valid, optuna_random_forest.predict_proba(X_valid)[:,1])
    f1_score = metrics.f1_score(y_valid, optuna_random_forest.predict(X_valid))
    recall_1 = metrics.recall_score(y_valid, optuna_random_forest.predict(X_valid),average=None,zero_division=0)[1]
    precision_1 = metrics.precision_score(y_valid, optuna_random_forest.predict(X_valid),average=None,zero_division=0)[1]

    # удаляем крупные файлы чтобы высвободить память 
    del X_train, X_valid, y_train, y_valid 
    gc.collect()

  except func_timeout.FunctionTimedOut:
    # освободим память от "тяжелых" и ненужных файлов
    del X_train_balanced, y_train_balanced
    gc.collect()

    # обьявим метрики пустыми значениями
    roc_train = 0
    roc_valid = 0
    f1_score = 0
    recall_1 = 0
    precision_1 = 0
    pass

  return roc_train, roc_valid, f1_score, recall_1, precision_1

In [1610]:
# так как Random Forest склонен к переобучению 
# попробуем направить optimize в сторону уменьшения roc_train
# cоздаем объект исследования
optuna_study_rf = optuna.create_study(study_name='RandomForestClassifier_'+feature_space+'_torow', 
                               directions=['minimize','maximize','maximize','maximize','maximize'], 
                               sampler=optuna.samplers.TPESampler(),
                               pruner='Hyperband',
                               storage='sqlite:///optuna_studies.db',
                               load_if_exists=True)
# на случай удаления 
# optuna.delete_study(study_name='RandomForestClassifier_'+feature_space+'_torow', storage='sqlite:///optuna_studies.db')

[I 2025-04-19 14:22:21,666] Using an existing study with name 'RandomForestClassifier_payments_torow' instead of creating a new one.


In [458]:
# ищем лучшую комбинацию гиперпараметров n_trials раз
optuna_study_rf.optimize(optuna_rf, n_trials=300)

[I 2025-04-17 16:02:26,229] Trial 0 finished with values: [0.6868456528972589, 0.670385773736389, 0.06787520507640367, 1.0, 0.03512982456140351] and parameters: {'n_estimators': 50, 'criterion': 'entropy', 'max_depth': 11, 'min_samples_split': 13, 'min_samples_leaf': 20, 'max_features': 0.19867254128901785, 'max_samples': 0.30115683984705166, 'class_0_weight': 0.4470996995030559, 'class_1_weight': 0.7129575862863762, 'n_last': 25, 'class_1_percent': 0.7722710181361001, 'random_state': 582625}.
[I 2025-04-17 16:02:38,740] Trial 1 finished with values: [0.740143041430384, 0.6704699498571371, 0.06949482500245095, 0.9912105473431881, 0.036009753548724203] and parameters: {'n_estimators': 80, 'criterion': 'gini', 'max_depth': 15, 'min_samples_split': 12, 'min_samples_leaf': 22, 'max_features': 0.2555083097676776, 'max_samples': 0.8814766798297707, 'class_0_weight': 0.13010288976040854, 'class_1_weight': 0.8549883878619666, 'n_last': 23, 'class_1_percent': 0.3955182771468322, 'random_state':

In [1611]:
# из полученного результат соврмируем Data Frame
optuna_study_rf_pd = optuna_study_rf.trials_dataframe().dropna()
# переименуем столбы
optuna_study_rf_pd.rename(columns={
    'values_0': 'roc_train',
    'values_1': 'roc_valid',
    'values_2': 'f1_score',
    'values_3': 'recall_1',
    'values_4': 'precision_1'
},inplace=True)
optuna_study_rf_pd.sort_values(by='precision_1').drop(['datetime_start','datetime_complete','duration'],axis=1)

number  roc_train  roc_valid  f1_score  recall_1  precision_1  \
123     123   0.691765   0.676197  0.000000  0.000000     0.000000   
218     218   0.708947   0.671121  0.000000  0.000000     0.000000   
272     272   0.740437   0.682411  0.000000  0.000000     0.000000   
133     133   0.697281   0.676461  0.000000  0.000000     0.000000   
96       96   0.679801   0.666143  0.000000  0.000000     0.000000   
..      ...        ...        ...       ...       ...          ...   
65       65   0.694443   0.673564  0.000797  0.000400     0.166667   
157     157   0.716306   0.678765  0.004730  0.002397     0.176471   
37       37   0.733420   0.681502  0.005525  0.002797     0.225806   
47       47   0.758277   0.678948  0.007859  0.003995     0.238095   
188     188   0.721907   0.680951  0.000798  0.000400     0.333333   

     params_class_0_weight  params_class_1_percent  params_class_1_weight  \
123               0.836395                0.317900               0.139781   
218               0.807779                0.453361               0.010952   
272               0.847125                0.115825               0.506162   
133               0.535542                0.333702               0.090639   
96                0.835618                0.611366               0.022919   
..                     ...                     ...                    ...   
65                0.964828                0.478012               0.092191   
157               0.784248                0.383776               0.148819   
37                0.918181                0.378280               0.198798   
47                0.185292                0.145829               0.174112   
188               0.767286                0.175377               0.467556   

    params_criterion  params_max_depth  params_max_features  \
123          entropy                 9             0.875485   
218             gini                13             0.641791   
272          entropy                15             0.843476   
133          entropy                11             0.810255   
96              gini                15             0.246090   
..               ...               ...                  ...   
65              gini                10             0.256096   
157          entropy                11             0.402695   
37          log_loss                15             0.704913   
47          log_loss                12             0.683333   
188          entropy                18             0.858008   

     params_max_samples  params_min_samples_leaf  params_min_samples_split  \
123            0.151606                       12                         9   
218            0.991138                       18                         9   
272            0.147383                       16                         5   
133            0.122118                       15                         9   
96             0.130971                       23                         6   
..                  ...                      ...                       ...   
65             0.383208                       23                        10   
157            0.770433                       16                         5   
37             0.875715                       21                        13   
47             0.740782                        7                         6   
188            0.139529                       17                         7   

     params_n_estimators  params_n_last  params_random_state     state  
123                   60             24               482358  COMPLETE  
218                  145             23                45836  COMPLETE  
272                  140             11               251227  COMPLETE  
133                  145             25               172438  COMPLETE  
96                    70             16               786537  COMPLETE  
..                   ...            ...                  ...       ...  
65                   105          

In [1612]:
# покаждем статистику обучения
print('Максимальное значение метрики ROC AUC на валидационном наборе:',round(optuna_study_rf_pd['roc_valid'].max(),3))
print('Среднее значение метрики ROC AUC на валидационном наборе:',round(optuna_study_rf_pd['roc_valid'].mean(),3))
print('Максимальное значение метрики f1_score на валидационном наборе:',round(optuna_study_rf_pd['f1_score'].max(),3))
print('Среднее значение метрики f1_score на валидационном наборе:',round(optuna_study_rf_pd['f1_score'].mean(),3))
print('Максимальное значение метрики recall_1 на валидационном наборе:',round(optuna_study_rf_pd['recall_1'].max(),3))
print('Среднее значение метрики recall_1 на валидационном наборе:',round(optuna_study_rf_pd['recall_1'].mean(),3))
print('Максимальное значение метрики precision_1 на валидационном наборе:',round(optuna_study_rf_pd['precision_1'].max(),3))
print('Среднее значение метрики precision_1 на валидационном наборе:',round(optuna_study_rf_pd['precision_1'].mean(),3))

Максимальное значение метрики ROC AUC на валидационном наборе: 0.682
Среднее значение метрики ROC AUC на валидационном наборе: 0.669
Максимальное значение метрики f1_score на валидационном наборе: 0.139
Среднее значение метрики f1_score на валидационном наборе: 0.089
Максимальное значение метрики recall_1 на валидационном наборе: 1.0
Среднее значение метрики recall_1 на валидационном наборе: 0.49
Максимальное значение метрики precision_1 на валидационном наборе: 0.333
Среднее значение метрики precision_1 на валидационном наборе: 0.069


In [1614]:
# Построим зависимость метрик качества модели от number

fig = px.scatter(
    data_frame=optuna_study_rf_pd[(optuna_study_rf_pd['roc_valid']>=0.68) 
                                  & (optuna_study_rf_pd['f1_score']>0.1)
                                  & (optuna_study_rf_pd['precision_1']>0.1)],
    x='number', #ось абсцисс
    y=['roc_valid','roc_train','precision_1','recall_1','f1_score'], #ось ординат
)
fig.update_layout(
    title ={
        'text':'Зависимость метрик качества модели от number', # Имя рабочей плоскости
        'font':{'size':35,'family':"Times New Roman"}, # размер и стиль написания имени рабочей плоскости
        'x':0.5, # Смешение имени по оси "x" на половину рабочей плоскости
        },
    height =800,# Высота рабочей плоскости
    width = 1350, # Ширина рабочей плоскости
    bargap=0.2, # Добавил расстояния между столбами гистограммы
    xaxis_title='Величина метрики ROC Valid',
    yaxis_title='Величина параметра')
fig.update_xaxes(showspikes=True)
fig.update_yaxes(showspikes=True)

fig.show()

<span style="color:Blue">

Вывод:  

Их всех выбираем точку $number =110$.   
В этой точке оптимальные значения метрик $recall_1$ и $precision_1$, а  
также относительно высокая метрика $ROC AUC$.   
Посмотрим каким значениям гиперпараметров соотвествует выбраннаяточка.

In [1615]:
# определим номер лучшге варианта
best_optuna_number = 110

# сформируем словарь лучших гипирпарметров RandomForestClassifier
best_param_rf = {
    'n_estimators' : int(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_n_estimators'].iloc[0]),
    'criterion': optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_criterion'].iloc[0],
    'max_depth' : optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_max_depth'].iloc[0],
    'min_samples_split': optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_min_samples_split'].iloc[0],
    'min_samples_leaf' : optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_min_samples_leaf'].iloc[0],
    'max_features': optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_max_features'].iloc[0],
    'max_samples' : optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_max_samples'].iloc[0],
    'class_weight' : {0:optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_class_0_weight'].iloc[0],
                      1:optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_class_1_weight'].iloc[0]}
    }
# определим перменные для лучших значений параметров
best_n_last = optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_n_last'].iloc[0]
best_class_1_percent = optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_class_1_percent'].iloc[0]
best_random_state = optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_random_state'].iloc[0]


# Выведем принятые наилучшие праметры
print('best n estimators:',best_param_rf['n_estimators'])
print('best criterion:',best_param_rf['criterion'])
print('best max depth:',best_param_rf['max_depth'])
print('best min samples split:',best_param_rf['min_samples_split'])
print('best min samples leaf:',best_param_rf['min_samples_leaf'])
print('best max features(%):',round(best_param_rf['max_features'],3))
print('best max samples(%):',round(best_param_rf['max_samples'],3))
print('best class 0 weight:',round(best_param_rf['class_weight'][0],3))
print('best class 1 weight:',round(best_param_rf['class_weight'][1],3))

print('best class 1 percent:',round(best_class_1_percent,3))
print('best n last:',best_n_last)
print('best random state:',best_random_state)
print('time for best train:',round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['duration'].iloc[0].seconds/60),'minutes')

print()
print('ROC AUC на обучающем наборе:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['roc_train'].iloc[0],3))
print('ROC AUC на валидационном наборе:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['roc_valid'].iloc[0],3))
print('precision класса 1:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['precision_1'].iloc[0],3))
print('recall класса 1:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['recall_1'].iloc[0],3))

best n estimators: 145
best criterion: entropy
best max depth: 12
best min samples split: 5
best min samples leaf: 16
best max features(%): 0.85
best max samples(%): 0.43
best class 0 weight: 0.777
best class 1 weight: 0.527
best class 1 percent: 0.391
best n last: 23
best random state: 868419
time for best train: 0 minutes

ROC AUC на обучающем наборе: 0.719
ROC AUC на валидационном наборе: 0.682
precision класса 1: 0.108
recall класса 1: 0.189


##### <span style="color:MediumSlateBlue">Обучение модели с лучшими параметрами</span>

In [468]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'payments'
count_features = dict_spaces[feature_space]

# с помощью функции features_from_transform_data_torow извлечем  
# из данных transform_data_torow
# признаки сооствествующие n_last последним клиенским операциям
list_n_last_features = features_from_transform_data_torow(best_n_last,count_features,25)

# загружаем обучующие наборы
X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)

# подготовим данные для обучения модели
# с помощью функции class_1_percent_samples зададим долю 
# класса 1
list_c1_percent_id = class_1_percent_samples(y_train_pd,best_class_1_percent,random_state=best_random_state)[:1000000]

# сформируем данные для обучения базовой модели
X_train_balanced = np.array(X_train_pd.loc[list_c1_percent_id])[:,list_n_last_features]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

# освободим память от "тяжелых" и ненужных файлов
del X_train_pd, y_train_pd
gc.collect()

# обучаем модель RandomForestClassifier с наилучшеми параметрами
random_forest = RandomForestClassifier(
        **best_param_rf,
        n_jobs=-1,
        random_state=best_random_state)
random_forest.fit(X_train_balanced, y_train_balanced)

# освободим память от "тяжелых" и ненужных файлов
del X_train_balanced, y_train_balanced
gc.collect()


# подгружаем данные для тестирования
X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()[:,list_n_last_features]
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()[:,list_n_last_features]
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_rf__pred_proba = random_forest.predict_proba(X_train)[:,1]
y_valid_rf_pred_proba = random_forest.predict_proba(X_valid)[:,1]

# Делаем предсказание для валидационной выборки
y_valid_rf_pred = random_forest.predict(X_valid)

# удаляем крупные файлы чтобы высвободить память 
del X_train, X_valid
gc.collect()

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_rf__pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_rf_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_rf_pred,zero_division=0))

# time: 2m 10s

ROC AUC на обучающем наборе 0.688
ROC AUC на валидационном наборе 0.67
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.99      0.16      0.28     68747
           1       0.04      0.95      0.08      2503

    accuracy                           0.19     71250
   macro avg       0.51      0.55      0.18     71250
weighted avg       0.95      0.19      0.27     71250



#### <span style="color:MediumBlue">Построение модели Gradient Boosting Classifier</span>

##### <span style="color:MediumSlateBlue">Формирование данных для обучения</span>

Анализ исходных данных, в частности target, показал что представленные данные   
имееют перекос: 96% клиентов у которых не случился дефолт (flag = 0),    
против 4 % - для которых произошел дефолт (flag = 1).  
С помощью функции class_1_percent_samples, сформируем сбаланисрованную выборку  
для обучения моделей.
За основу сбалансировных данных возьмем данные клиентов с дефолтом  
и к ним будем добирать необходимое количество клиентов до сбалансированности. 


Функция class_1_percent_samples принемает две переменные:
- target_data - массив с id и целевой переменной
- class_1_percent - процент класса 1 в результирующем массиве

In [476]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'service'
count_features = dict_spaces[feature_space]

In [477]:
# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

In [478]:
# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)
y_train_pd.head(4)

id  flag
id                    
1825800  1825800     0
2166483  2166483     0
2534345  2534345     0
1803283  1803283     0

In [479]:
# взглянем на сблансиорованность данных в y_train
y_train_pd['flag'].value_counts(normalize=True)

flag
0    0.964242
1    0.035758
Name: proportion, dtype: float64

In [480]:
# сбалансируем данные в y_train_pd
list_c1_percent_id = class_1_percent_samples(y_train_pd,0.5)
# list_c1_percent_features - список 'id' из y_train_pd соотвествующих  
# заданному проценту класса 1
len(list_c1_percent_id)

45860

In [481]:
# проверим сбалансированность полученного y_train
y_train_pd.loc[list_c1_percent_id]['flag'].value_counts(normalize=True)

flag
1    0.5
0    0.5
Name: proportion, dtype: float64

*transform_data_torow*, показываеются последние N операций клиента.  
В данных в *date_torow*, собраны последние 25 операций клиентов.

Предварительный анализ показывает, что медиальное значение количества клиентских  
операций равно 7. Поэтому, для начала, будем показывать моделе $n_{last} = 7$   
последних клиентских операций.

Для извлечения из *transform_data_torow_25* необходимого количества последних клиенских  
операций ($n_{last}$) используем функцию features_from_transform_data_torow.

Функция features_from_transform_data_torow примает следующие аргументы:
- $n_{last} = 7$ - необходимое количество последних клиентских операций; 
- $n_{groups} = 8$ - количество признаков в $date$ $features$;
- $N_{last} = 25$ - количество $n_{last}$ операций, показанных в transform_data_torow_25


In [482]:
# с помощью функции features_from_transform_data_torow извлечем  
# из данных transform_data_torow_25
# признаки сооствествующие 7 последним клиенским операциям
list_n_last_features = features_from_transform_data_torow(7,count_features,25)

In [483]:
# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']
# сформируем данные для проверики модели
X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

In [484]:
# посмотрим на структуру данных в X_train_balanced
X_train_balanced.head(2)

f1  f2  f3  f4  f5  f6  f7  f8  f9  f10  ...  f91  f92  f93  f94  \
id                                                ...                       
2335465   1   1   1   1   1   1   1   1   1    1  ...    1    1    0    0   
390270    1   1   1   1   1   1   0   0   0    0  ...    0    0    0    0   

         f95  f96  f97  f98  f99  f100  
id                                      
2335465    0    0    0    0    0     0  
390270     0    0    0    0    0     0  

[2 rows x 100 columns]

In [485]:
# посмотрим на структуру данных в y_train_balanced
y_train_balanced.head(2)

id
2335465    1
390270     1
Name: flag, dtype: int64

In [486]:
# проверим что выборки действительно совпадают по id
X_train_balanced.index.to_list() == y_train_balanced.index.to_list()

True

##### <span style="color:MediumSlateBlue">Baseline обучение модели Hist Gradient Boosting Classifier</span>

In [487]:
# обучаем модель Gradient Boosting Classifier
gradient_boosting = HistGradientBoostingClassifier(random_state=42)
gradient_boosting.fit(np.array(X_train_balanced)[:,list_n_last_features],np.array(y_train_balanced))

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_rf__pred_proba = gradient_boosting.predict_proba(X_train[:,list_n_last_features])[:,1]
y_valid_rf_pred_proba = gradient_boosting.predict_proba(X_valid[:,list_n_last_features])[:,1]

# Делаем предсказание для валидационной выборки
y_valid_rf_pred = gradient_boosting.predict(X_valid[:,list_n_last_features])

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_rf__pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_rf_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_rf_pred))

# time: 

ROC AUC на обучающем наборе 0.651
ROC AUC на валидационном наборе 0.633
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.98      0.62      0.76     68747
           1       0.05      0.57      0.10      2503

    accuracy                           0.62     71250
   macro avg       0.51      0.60      0.43     71250
weighted avg       0.94      0.62      0.73     71250



##### <span style="color:MediumSlateBlue">Подбор гиперпараметров модели</span>

In [1616]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'payments'
count_features = dict_spaces[feature_space]

# настроим оптимизацию гипер параметров
def optuna_hgbc(trial):
  # задаем пространства поиска гиперпараметров
  learning_rate = trial.suggest_float('learning_rate',0.2,0.6)
  max_iter = trial.suggest_int('max_iter', 50, 300,step = 1)
  max_leaf_nodes = trial.suggest_int('max_leaf_nodes', 2, 50,step = 1)
  max_depth = trial.suggest_int('max_depth', 1, 15,step = 1)
  min_samples_leaf = trial.suggest_int('min_samples_leaf', 1, 50,step = 1)
  max_features = trial.suggest_float('max_features',0.1,1)
  l2_regularization = trial.suggest_float('l2_regularization',0.01,1)
  class_0_weight = trial.suggest_float('class_0_weight',0.01,1)
  class_1_weight = trial.suggest_float('class_1_weight',0.01,1)
  n_last = trial.suggest_int('n_last', 5, 25,step = 1)
  class_1_percent = trial.suggest_float('class_1_percent',0.01,1)
  random_state = trial.suggest_int('random_state', 1, 1000000)


  # создаем модель
  optuna_gradient_boosting = HistGradientBoostingClassifier(
      learning_rate= learning_rate,
      max_iter = max_iter,
      max_leaf_nodes =max_leaf_nodes,
      max_depth = max_depth,
      min_samples_leaf = min_samples_leaf,
      max_features=max_features,
      l2_regularization = l2_regularization,
      class_weight={0:class_0_weight,1:class_1_weight},
      random_state=42)

  # с помощью функции features_from_transform_data_torow извлечем  
  # из данных transform_data_torow
  # признаки сооствествующие n_last последним клиенским операциям
  list_n_last_features = features_from_transform_data_torow(n_last,count_features,25)

  # загружаем обучующие наборы
  X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
  y_train_pd = pd.read_csv('target/target_train.csv')

  # поготовим данные y_train_pd к работе с функцией class_1_percent_samples
  y_train_pd.set_index('id',drop=False,inplace=True)

  # подготовим данные для обучения модели
  # с помощью функции class_1_percent_samples зададим долю класса 1
  list_c1_percent_id = class_1_percent_samples(y_train_pd,class_1_percent,random_state=random_state)[:1000000]

  # сформируем данные для обучения модели
  X_train_balanced = np.array(X_train_pd.loc[list_c1_percent_id])[:,list_n_last_features]
  y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

  # освободим память от "тяжелых" и ненужных файлов
  del X_train_pd, y_train_pd
  gc.collect()

  # я не воспользовался параметром timeout метода optimize потому, что  
  # optimize отставливает поиск параметров, если время обучения 
  # превышает timeout. Мне нужно чтобы поиск параметров продолжился.
  try:
    # для модуля func_time_out упакуем обучение модели в функцию try_func
    def try_func():
            return optuna_gradient_boosting.fit(X_train_balanced,y_train_balanced)
    # обучаем модель с ограничением по времени 10 минут (600 секунд)
    optuna_gradient_boosting = func_timeout.func_timeout(600, try_func)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train_balanced, y_train_balanced
    gc.collect()

    # подгружаем данные для тестирования
    X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()[:,list_n_last_features]
    y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
    X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()[:,list_n_last_features]
    y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

    # делаем предсказание на обучающем и валидационном наборе и считаем метрики
    roc_train = metrics.roc_auc_score(y_train, optuna_gradient_boosting.predict_proba(X_train)[:,1])
    roc_valid = metrics.roc_auc_score(y_valid, optuna_gradient_boosting.predict_proba(X_valid)[:,1])
    f1_score = metrics.f1_score(y_valid, optuna_gradient_boosting.predict(X_valid))
    recall_1 = metrics.recall_score(y_valid, optuna_gradient_boosting.predict(X_valid),average=None,zero_division=0)[1]
    precision_1 = metrics.precision_score(y_valid, optuna_gradient_boosting.predict(X_valid),average=None,zero_division=0)[1]

    # удаляем крупные файлы чтобы высвободить память 
    del X_train, X_valid, y_train, y_valid 
    gc.collect()

  except func_timeout.FunctionTimedOut:
    # освободим память от "тяжелых" и ненужных файлов
    del X_train_balanced, y_train_balanced
    gc.collect()

    # обьявим метрики пустыми значениями
    roc_train = 0
    roc_valid = 0
    f1_score = 0
    recall_1 = 0
    precision_1 = 0
    pass

  return roc_train, roc_valid, f1_score, recall_1, precision_1

In [1617]:
# cоздаем объект исследования
# чтобы модель не переобучалась минимизируем roc_train 
# и максимизируем roc_valid
optuna_study_hsbs = optuna.create_study(study_name='HistGradientBoostingClassifier_'+feature_space+'_torow', 
                               directions=['maximize','maximize','maximize','maximize','maximize'], 
                               sampler=optuna.samplers.TPESampler(),
                               pruner='Hyperband',
                               storage='sqlite:///optuna_studies.db',
                               load_if_exists=True)

# ну случай удаления обучения
# optuna.delete_study(study_name='HistGradientBoostingClassifier_'+feature_space+'_torow', storage='sqlite:///optuna_studies.db')

[I 2025-04-19 14:24:27,546] Using an existing study with name 'HistGradientBoostingClassifier_payments_torow' instead of creating a new one.


In [490]:
# ищем лучшую комбинацию гиперпараметров n_trials раз
optuna_study_hsbs.optimize(optuna_hgbc, n_trials=300)

[I 2025-04-17 17:14:34,352] Trial 0 finished with values: [0.652640384546915, 0.6451128792509951, 0.0682492176075875, 0.9976028765481423, 0.03533323899816047] and parameters: {'learning_rate': 0.5533352391219629, 'max_iter': 78, 'max_leaf_nodes': 8, 'max_depth': 12, 'min_samples_leaf': 30, 'max_features': 0.3661937684278576, 'l2_regularization': 0.242176900727974, 'class_0_weight': 0.562160357724473, 'class_1_weight': 0.21942882420927956, 'n_last': 19, 'class_1_percent': 0.9448392149060463, 'random_state': 470175}.
[I 2025-04-17 17:14:41,400] Trial 1 finished with values: [0.670925193659541, 0.6654399813391632, 0.02539912917271408, 0.013983220135836995, 0.1383399209486166] and parameters: {'learning_rate': 0.3774445733655174, 'max_iter': 158, 'max_leaf_nodes': 31, 'max_depth': 1, 'min_samples_leaf': 31, 'max_features': 0.3750247556898419, 'l2_regularization': 0.3023449713237821, 'class_0_weight': 0.8161159805501661, 'class_1_weight': 0.10586590129811949, 'n_last': 12, 'class_1_percent'

In [1618]:
# из полученного результат соврмируем Data Frame
optuna_study_hsbs_pd = optuna_study_hsbs.trials_dataframe()
# переименуем столбы
optuna_study_hsbs_pd.rename(columns={
    'values_0': 'roc_train',
    'values_1': 'roc_valid',
    'values_2': 'f1_score',
    'values_3': 'recall_1',
    'values_4': 'precision_1'
},inplace=True)
# Выделим время потраченное на обучение модели
last_trail = optuna_study_hsbs_pd['number'].max()
optuna_study_hsbs_pd.tail(5)


number  roc_train  roc_valid  f1_score  recall_1  precision_1  \
295     295   0.708868   0.680112  0.073766  0.955653     0.038363   
296     296   0.705579   0.681869  0.000793  0.000400     0.052632   
297     297   0.715446   0.684455  0.138284  0.285657     0.091222   
298     298   0.713614   0.678919  0.095280  0.085897     0.106965   
299     299   0.706441   0.679636  0.083366  0.883340     0.043748   

                datetime_start          datetime_complete  \
295 2025-04-17 18:20:50.621391 2025-04-17 18:21:03.872181   
296 2025-04-17 18:21:03.877981 2025-04-17 18:21:22.044343   
297 2025-04-17 18:21:22.049518 2025-04-17 18:21:36.771127   
298 2025-04-17 18:21:36.777045 2025-04-17 18:21:49.548652   
299 2025-04-17 18:21:49.554015 2025-04-17 18:22:02.644440   

                  duration  params_class_0_weight  ...  \
295 0 days 00:00:13.250790               0.244919  ...   
296 0 days 00:00:18.166362               0.274468  ...   
297 0 days 00:00:14.721609               0.227440  ...   
298 0 days 00:00:12.771607               0.286828  ...   
299 0 days 00:00:13.090425               0.673501  ...   

     params_l2_regularization  params_learning_rate  params_max_depth  \
295                  0.255446              0.262767                14   
296                  0.222321              0.294900                15   
297                  0.262173              0.223702                15   
298                  0.791873              0.360941                14   
299                  0.290875              0.270627                15   

     params_max_features  params_max_iter  params_max_leaf_nodes  \
295             0.961381              105                     36   
296             0.864684               80                     31   
297             0.748283               99                     30   
298             0.886349               66                     35   
299             0.923846              119                     37   

     params_min_samples_leaf  params_n_last  params_random_state     state  
295                       44             22               340967  COMPLETE  
296                       46              5                70667  COMPLETE  
297                       47             13               110402  COMPLETE  
298                       38             11                64283  COMPLETE  
299                       48             22               151675  COMPLETE  

[5 rows x 22 columns]

In [1619]:
# покаждем статистику обучения
print('Максимальное значение метрики ROC AUC на валидационном наборе:',round(optuna_study_hsbs_pd['roc_valid'].max(),3))
print('Среднее значение метрики ROC AUC на валидационном наборе:',round(optuna_study_hsbs_pd['roc_valid'].mean(),3))
print('Максимальное значение метрики f1_score на валидационном наборе:',round(optuna_study_hsbs_pd['f1_score'].max(),3))
print('Среднее значение метрики f1_score на валидационном наборе:',round(optuna_study_hsbs_pd['f1_score'].mean(),3))
print('Максимальное значение метрики recall_1 на валидационном наборе:',round(optuna_study_hsbs_pd['recall_1'].max(),3))
print('Среднее значение метрики recall_1 на валидационном наборе:',round(optuna_study_hsbs_pd['recall_1'].mean(),3))
print('Максимальное значение метрики precision_1 на валидационном наборе:',round(optuna_study_hsbs_pd['precision_1'].max(),3))
print('Среднее значение метрики precision_1 на валидационном наборе:',round(optuna_study_hsbs_pd['precision_1'].mean(),3))

Максимальное значение метрики ROC AUC на валидационном наборе: 0.688
Среднее значение метрики ROC AUC на валидационном наборе: 0.678
Максимальное значение метрики f1_score на валидационном наборе: 0.142
Среднее значение метрики f1_score на валидационном наборе: 0.096
Максимальное значение метрики recall_1 на валидационном наборе: 1.0
Среднее значение метрики recall_1 на валидационном наборе: 0.418
Максимальное значение метрики precision_1 на валидационном наборе: 1.0
Среднее значение метрики precision_1 на валидационном наборе: 0.082


In [1630]:
# Построим зависимость метрик качества модели от number

fig = px.scatter(
    data_frame=optuna_study_hsbs_pd[(optuna_study_hsbs_pd['roc_valid']>0.9999*optuna_study_hsbs_pd['roc_valid'].max())],
    x='number', #ось абсцисс
    y=['roc_train','roc_valid','recall_1','precision_1','f1_score'], #ось ординат
)
fig.update_layout(
    title ={
        'text':'Зависимость precision от гиперпараметров модели', # Имя рабочей плоскости
        'font':{'size':35,'family':"Times New Roman"}, # размер и стиль написания имени рабочей плоскости
        'x':0.5, # Смешение имени по оси "x" на половину рабочей плоскости
        },
    height =800,# Высота рабочей плоскости
    width = 1350, # Ширина рабочей плоскости
    bargap=0.2, # Добавил расстояния между столбами гистограммы
    xaxis_title='Величина метрики precision_1',
    yaxis_title='Величина параметра')
fig.update_xaxes(showspikes=True)
fig.update_yaxes(showspikes=True)

fig.show()

<span style="color:Blue">

Вывод:  

Их всех выбираем точку $number =160$.   
В этой точке оптимальные значения метрик $recall_1$ и $precision_1$, а  
также относительно высокая метрика $ROC AUC$.   
Посмотрим каким значениям гиперпараметров соотвествует выбранная точка.

In [1631]:
# определим номер лучшге варианта
best_optuna_number = 160

# сформируем словарь лучших гипирпарметров RandomForestClassifier
best_param_rf = {
    'learning_rate' : optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_learning_rate'].iloc[0],
    'max_iter' : optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_max_iter'].iloc[0],
    'max_leaf_nodes' : optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_max_leaf_nodes'].iloc[0],
    'max_depth' : optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_max_depth'].iloc[0],
    'min_samples_leaf' : optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_min_samples_leaf'].iloc[0],
    'max_features' : optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_max_features'].iloc[0],
    'l2_regularization' : optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_l2_regularization'].iloc[0],
    'class_weight' : {0: optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_class_0_weight'].iloc[0],
                      1: optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_class_1_weight'].iloc[0],}
    }

# определим перменные для лучших значений параметров
best_n_last = optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_n_last'].iloc[0]
best_class_1_percent = optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_class_1_percent'].iloc[0]
best_random_state = optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_random_state'].iloc[0]


# Выведем принятые наилучшие праметры
print('best learning rate:',round(best_param_rf['learning_rate'],3))
print('best max iter:',best_param_rf['max_iter'])
print('best max leaf nodes:',best_param_rf['max_leaf_nodes'])
print('best max depth:',best_param_rf['max_depth'])
print('best min samples leaf:',best_param_rf['min_samples_leaf'])
print('best max features:',round(best_param_rf['max_features'],3))
print('best l2 regularization:',round(best_param_rf['l2_regularization'],3))
print('best class 0 weight:',round(best_param_rf['class_weight'][0],3))
print('best class 1 weight:',round(best_param_rf['class_weight'][1],3))

print('best class 1 percent:',round(best_class_1_percent,3))
print('best n last:',best_n_last)
print('best random state:',best_random_state)
print('time for best train:',round(optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['duration'].iloc[0].seconds/60),'minutes')

print()
print('ROC AUC на обучающем наборе:', round(optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['roc_train'].iloc[0],3))
print('ROC AUC на валидационном наборе:', round(optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['roc_valid'].iloc[0],3))
print('precision класса 1:', round(optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['precision_1'].iloc[0],3))
print('recall класса 1:', round(optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['recall_1'].iloc[0],3))

best learning rate: 0.242
best max iter: 212
best max leaf nodes: 24
best max depth: 15
best min samples leaf: 49
best max features: 0.769
best l2 regularization: 0.248
best class 0 weight: 0.297
best class 1 weight: 0.532
best class 1 percent: 0.098
best n last: 25
best random state: 3648
time for best train: 0 minutes

ROC AUC на обучающем наборе: 0.713
ROC AUC на валидационном наборе: 0.688
precision класса 1: 0.146
recall класса 1: 0.016


##### <span style="color:MediumSlateBlue">Обучение модели с лучшими параметрами</span>

In [501]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'payments'
count_features = dict_spaces[feature_space]

# с помощью функции features_from_transform_data_torow извлечем  
# из данных transform_data_torow
# признаки сооствествующие n_last последним клиенским операциям
list_n_last_features = features_from_transform_data_torow(best_n_last,count_features,25)

# загружаем обучующие наборы
X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)

# подготовим данные для обучения модели
# с помощью функции class_1_percent_samples зададим долю класса 1
list_c1_percent_id = class_1_percent_samples(y_train_pd,best_class_1_percent,random_state=best_random_state)[:1000000]

# сформируем данные для обучения модели
X_train_balanced = np.array(X_train_pd.loc[list_c1_percent_id])[:,list_n_last_features]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

# освободим память от "тяжелых" и ненужных файлов
del X_train_pd, y_train_pd
gc.collect()


# обучаем модель HistGradientBoostingClassifier с наилучшеми параметрами
gradient_boosting = HistGradientBoostingClassifier(
        **best_param_rf,
        random_state=42)
gradient_boosting.fit(X_train_balanced,y_train_balanced)

# освободим память от "тяжелых" и ненужных файлов
del X_train_balanced, y_train_balanced
gc.collect()

# подгружаем данные для тестирования
X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()[:,list_n_last_features]
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()[:,list_n_last_features]
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_gb__pred_proba = gradient_boosting.predict_proba(X_train)[:,1]
y_valid_gb_pred_proba = gradient_boosting.predict_proba(X_valid)[:,1]

# Делаем предсказание для валидационной выборки
y_valid_gb_pred = gradient_boosting.predict(X_valid)

# освободим память от "тяжелых" и ненужных файлов
del X_train, X_valid
gc.collect()

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_gb__pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_gb_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_gb_pred,zero_division=0))

# time: 2m 30s

ROC AUC на обучающем наборе 0.706
ROC AUC на валидационном наборе 0.687
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.98      0.78      0.87     68747
           1       0.07      0.48      0.13      2503

    accuracy                           0.77     71250
   macro avg       0.52      0.63      0.50     71250
weighted avg       0.94      0.77      0.84     71250



### <span style="color:RoyalBlue">Построение модели на сбалансированных данных подпространства service torow</span>

#### <span style="color:MediumBlue">Построение модели Logistic Regression</span>

##### <span style="color:MediumSlateBlue">Формирование данных для обучения</span>

Анализ исходных данных, в частности target, показал что представленные данные   
имееют перекос: 96% клиентов у которых не случился дефолт (flag = 0),    
против 4 % - для которых произошел дефолт (flag = 1).  
С помощью функции class_1_percent_samples, сформируем сбаланисрованную выборку  
для обучения моделей.
За основу сбалансировных данных возьмем данные клиентов с дефолтом  
и к ним будем добирать необходимое количество клиентов до сбалансированности. 


Функция class_1_percent_samples принемает две переменные:
- target_data - массив с id и целевой переменной
- class_1_percent - процент класса 1 в результирующем массиве

In [509]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'service'
count_features = dict_spaces[feature_space]

In [510]:
# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

In [511]:
# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)
y_train_pd.head(4)

id  flag
id                    
1825800  1825800     0
2166483  2166483     0
2534345  2534345     0
1803283  1803283     0

In [512]:
# взглянем на сблансиорованность данных в y_train
y_train_pd['flag'].value_counts(normalize=True)

flag
0    0.964242
1    0.035758
Name: proportion, dtype: float64

In [513]:
# сбалансируем данные в y_train_pd
list_c1_percent_id = class_1_percent_samples(y_train_pd,0.5)
# list_c1_percent_features - список 'id' из y_train_pd соотвествующих  
# заданному проценту класса 1
len(list_c1_percent_id)

45860

In [514]:
# проверим сбалансированность полученного y_train
y_train_pd.loc[list_c1_percent_id]['flag'].value_counts(normalize=True)

flag
1    0.5
0    0.5
Name: proportion, dtype: float64

*transform_data_torow*, показываеются последние N операций клиента.  
В данных в *date_torow*, собраны последние 25 операций клиентов.

Предварительный анализ показывает, что медиальное значение количества клиентских  
операций равно 7. Поэтому, для начала, будем показывать моделе $n_{last} = 7$   
последних клиентских операций.

Для извлечения из *transform_data_torow_25* необходимого количества последних клиенских  
операций ($n_{last}$) используем функцию features_from_transform_data_torow.

Функция features_from_transform_data_torow примает следующие аргументы:
- $n_{last} = 7$ - необходимое количество последних клиентских операций; 
- $n_{groups} = 8$ - количество признаков в $date$ $features$;
- $N_{last} = 25$ - количество $n_{last}$ операций, показанных в transform_data_torow_25


In [515]:
# с помощью функции features_from_transform_data_torow извлечем  
# из данных transform_data_torow_25
# признаки сооствествующие 7 последним клиенским операциям
list_n_last_features = features_from_transform_data_torow(7,count_features,25)

In [516]:
# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']
# сформируем данные для проверики модели
X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

In [517]:
# посмотрим на структуру данных в X_train_balanced
X_train_balanced.head(2)

f1  f2  f3  f4  f5  f6  f7  f8  f9  f10  ...  f91  f92  f93  f94  \
id                                                ...                       
2335465   1   1   1   1   1   1   1   1   1    1  ...    1    1    0    0   
390270    1   1   1   1   1   1   0   0   0    0  ...    0    0    0    0   

         f95  f96  f97  f98  f99  f100  
id                                      
2335465    0    0    0    0    0     0  
390270     0    0    0    0    0     0  

[2 rows x 100 columns]

In [518]:
# посмотрим на структуру данных в y_train_balanced
y_train_balanced.head(2)

id
2335465    1
390270     1
Name: flag, dtype: int64

In [519]:
# проверим что выборки действительно совпадают по id
X_train_balanced.index.to_list() == y_train_balanced.index.to_list()

True

##### <span style="color:MediumSlateBlue">Baseline обучение модели LogisticRegression</span>

In [520]:
# обучаем модель логистической регрессии
logistic_regression = linear_model.LogisticRegression(random_state=42, max_iter=10000)
logistic_regression.fit(np.array(X_train_balanced)[:,list_n_last_features],np.array(y_train_balanced))

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_LR_pred_proba = logistic_regression.predict_proba(X_train[:,list_n_last_features])[:,1]
y_valid_LR_pred_proba = logistic_regression.predict_proba(X_valid[:,list_n_last_features])[:,1]

# Делаем предсказание для валидационной выборки
y_valid_LR_pred = logistic_regression.predict(X_valid[:,list_n_last_features])

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_LR_pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_LR_pred_proba),3))

print('Основные метрики на тестовом наборе:')
print(metrics.classification_report(y_valid,y_valid_LR_pred))

# time: 1m 12s

ROC AUC на обучающем наборе 0.592
ROC AUC на валидационном наборе 0.594
Основные метрики на тестовом наборе:
              precision    recall  f1-score   support

           0       0.97      0.53      0.69     68747
           1       0.05      0.61      0.08      2503

    accuracy                           0.54     71250
   macro avg       0.51      0.57      0.39     71250
weighted avg       0.94      0.54      0.67     71250



##### <span style="color:MediumSlateBlue">Анализ влияния scaler преобразования на качество и скорость схождения модели</span>

In [521]:
# формируем список из необходимых scaler
scalers = [MinMaxScaler(),RobustScaler() ,StandardScaler()]

# сформируем списко для заполнения данными результатов анализа
scalers_data = []

# установим ограничение на время обучения модели в 600 секунд (10 минут)
time_out = 600

for scaler in scalers:
        # для того чтобы следить за выполнением цикла введем индикатор
        print('current scaler: ', scaler)

         # сформируем список для заполнения данными текушего scaler
        current_scaler_data = [scaler]
        
        # выполним scaler преобразование
        X_train_s_balanced = scaler.fit_transform(np.array(X_train_balanced)[:,list_n_last_features])
        X_train_s = scaler.transform(X_train[:,list_n_last_features])
        X_valid_s = scaler.transform(X_valid[:,list_n_last_features])

        try:
                # для модуля func_time_out упакуем обучение модели в функцию try_func
                def try_func():
                        logistic_regression = linear_model.LogisticRegression(random_state=42, max_iter=10000)
                        return logistic_regression.fit(X_train_s_balanced,y_train_balanced)
                    
                # фиксируем время начала
                start_time = time.time()
                
                # запускаем обучение модели с ограничением по времени
                logistic_regression = func_timeout.func_timeout(time_out, try_func)
                
                # фиксируем время окончания обучения
                end_time = time.time()
                
                # запишем время обучения модели
                current_scaler_data.append(round(end_time-start_time))

                # Делаем предсказание для обучающей и валидационной выборки
                y_valid_lr_pred = logistic_regression.predict(X_valid_s)
                
                # для метрик ROC AUC делаем предсказание модели для обучающей и валидационной выборки  
                # в виде вероятности принадлежности к классу 1 
                y_train_lr_pred_proba = logistic_regression.predict_proba(X_train_s)[:,1]
                y_valid_lr_pred_proba = logistic_regression.predict_proba(X_valid_s)[:,1]

                #Считаем метрики ROC AUC yна обуающем и валидационном наборе и добавляем их в спискок
                current_scaler_data.append(round(metrics.roc_auc_score(y_train, y_train_lr_pred_proba),3))
                current_scaler_data.append(round(metrics.roc_auc_score(y_valid, y_valid_lr_pred_proba),3))

                #Считаем метрики для класса 0 на валидационном наборе и добавляем их в список
                current_scaler_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))
                current_scaler_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))


                #Считаем метрики для класса 1 на валидационном набопе и добавляем их в список
                current_scaler_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))
                current_scaler_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))

                # добавляем полученные данные в список scalers_data
                scalers_data.append(current_scaler_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                scaler_pd =pd.DataFrame(
                        columns=['scaler','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = scalers_data)
                # сохраняем dataframe
                scaler_pd.to_csv('data_recovery/scaler_pd.csv',index=False)
               
                # очистим output от прошедшей итерации
                clear_output()

        except func_timeout.FunctionTimedOut:
                # если время обучения привышает лимит
                # запишем в current_scaler_data соотвествующую данные
                current_scaler_data = [scaler,'>30m',0,0,0,0,0,0]
                # добавляем полученные данные в список scalers_data
                scalers_data.append(current_scaler_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                scaler_pd =pd.DataFrame(
                        columns=['scaler','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = scalers_data)
                # сохраняем dataframe
                scaler_pd.to_csv('data_recovery/scaler_pd.csv',index=False)
                
                # очистим output от прошедшей итерации
                clear_output()
                # переходим к следующему scaler
                pass
# очистим output
clear_output()

# сформируем данные соотвествующие лучщему ROC AUC на валидацинном наборе
best_roc_valid_data = scaler_pd[scaler_pd['roc_valid']==scaler_pd['roc_valid'].max()]

# выведем лучший результат на валидационном наборе
print('result:')
print('best scaler on valid:',best_roc_valid_data.iloc[0]['scaler'])
print('ROC AUC on train:', best_roc_valid_data.iloc[0]['roc_train'])
print('ROC AUC on valid:', best_roc_valid_data.iloc[0]['roc_valid'])
print('Time fit for best scaler:', best_roc_valid_data.iloc[0]['time_fit'],' seconds')

# выведем полученный dataframe
scaler_pd

# time: 

result:
best scaler on valid: RobustScaler()
ROC AUC on train: 0.592
ROC AUC on valid: 0.595
Time fit for best scaler: 0  seconds


scaler  time_fit  roc_train  roc_valid  recall_0  precision_0  \
0    MinMaxScaler()         0      0.592      0.594     0.533        0.974   
1    RobustScaler()         0      0.592      0.595     0.532        0.974   
2  StandardScaler()         0      0.592      0.594     0.532        0.974   

   recall_1  precision_1  
0     0.608        0.045  
1     0.608        0.045  
2     0.608        0.045

##### <span style="color:MediumSlateBlue"> Анализ влияния solver оптимизатора на качество и скорость обучения модели</span>

Проверим качество и скорость сходимости модели при разных solver  
Проверку осуществим через цикл  
Чтобы модель не сходилась бесконечно с помощью модуля func_timeout  
поставим ограничение времени схождения в 10 минут

In [522]:
# подготовим данные для обучения модели

# обьявим scaler
scaler = StandardScaler()
# выполним scaler преобразование
X_train_s_balanced = scaler.fit_transform(np.array(X_train_balanced)[:,list_n_last_features])
X_train_s = scaler.transform(X_train[:,list_n_last_features])
X_valid_s = scaler.transform(X_valid[:,list_n_last_features])

# time: 10s

In [523]:
# Зададим список solvers
solvers_list = ['lbfgs', 'liblinear', 'newton-cg', 'newton-cholesky', 'sag', 'saga']

# сформируем список для заполнения
solvers_data = []

# установим ограничение на время обучения модели в 300 секунд (5 минут)
time_out = 300

for solver in solvers_list:
        # для того чтобы следить за выполнением цикла введем индикатор
        print('current solver: ', solver)

         # сформируем список для заполнения данными текушего solver
        current_solver_data = [solver]
        
        try:
                # для модуля func_time_out упакуем обучение модели в функцию try_func
                def try_func():
                        logistic_regression = linear_model.LogisticRegression(solver= solver,
                                                                  random_state=42, 
                                                                  max_iter=10000)
                        return logistic_regression.fit(X_train_s_balanced,y_train_balanced)
                    
                # фиксируем время начала
                start_time = time.time()
                
                # запускаем обучение модели с ограничением по времени
                logistic_regression = func_timeout.func_timeout(time_out, try_func)
                
                # фиксируем время окончания обучения
                end_time = time.time()
                
                # запишем время обучения модели
                current_solver_data.append(round(end_time-start_time))

                # Делаем предсказание для обучающей и валидационной выборки
                y_valid_lr_pred = logistic_regression.predict(X_valid_s)
                
                # для метрик ROC AUC делаем предсказание модели для обучающей и валидационной выборки  
                # в виде вероятности принадлежности к классу 1 
                y_train_lr_pred_proba = logistic_regression.predict_proba(X_train_s)[:,1]
                y_valid_lr_pred_proba = logistic_regression.predict_proba(X_valid_s)[:,1]

                #Считаем метрики ROC AUC yна обуающем и валидационном наборе и добавляем их в спискок
                current_solver_data.append(round(metrics.roc_auc_score(y_train, y_train_lr_pred_proba),3))
                current_solver_data.append(round(metrics.roc_auc_score(y_valid, y_valid_lr_pred_proba),3))

                #Считаем метрики для класса 0 на валидационном наборе и добавляем их в список
                current_solver_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))
                current_solver_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))


                #Считаем метрики для класса 1 на валидационном набопе и добавляем их в список
                current_solver_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))
                current_solver_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))

                # запишем данные полученные на одной итерации
                solvers_data.append(current_solver_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                solvers_pd =pd.DataFrame(
                        columns=['solver','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = solvers_data)
                # сохраняем dataframe
                solvers_pd.to_csv('data_recovery/solvers_pd.csv',index=False)
               
                # очистим output от прошедшей итерации
                clear_output()

        except func_timeout.FunctionTimedOut:
                # если время обучения привышает лимит
                # запишем в current_solver_data соотвествующую данные
                current_solver_data = [solver,'>10m',0,0,0,0,0,0]
                # добавляем полученные данные в список solvers_data
                solvers_data.append(current_solver_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                solvers_pd =pd.DataFrame(
                        columns=['solver','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = solvers_data)
                # сохраняем dataframe
                solvers_pd.to_csv('data_recovery/solvers_pd.csv',index=False)
                
                # очистим output от прошедшей итерации
                clear_output()
                # переходим к следующему solver
                pass
# очистим output
clear_output()

# сформируем данные соотвествующие лучщему ROC AUC на валидацинном наборе
best_roc_valid_data = solvers_pd[solvers_pd['roc_valid']==solvers_pd['roc_valid'].max()]

# выведем лучший результат на валидационном наборе
print('result:')
print('best solver on valid:',best_roc_valid_data.iloc[0]['solver'])
print('ROC AUC on train:', best_roc_valid_data.iloc[0]['roc_train'])
print('ROC AUC on valid:', best_roc_valid_data.iloc[0]['roc_valid'])
print('Time fit for best solver:', best_roc_valid_data.iloc[0]['time_fit'],' seconds')

# выведем полученный dataframe
solvers_pd

# time: 11m 35s

result:
best solver on valid: newton-cg
ROC AUC on train: 0.592
ROC AUC on valid: 0.595
Time fit for best solver: 0  seconds


solver  time_fit  roc_train  roc_valid  recall_0  precision_0  \
0            lbfgs         0      0.592      0.594     0.532        0.974   
1        liblinear         0      0.592      0.594     0.532        0.974   
2        newton-cg         0      0.592      0.595     0.532        0.974   
3  newton-cholesky         0      0.592      0.594     0.532        0.974   
4              sag         0      0.592      0.594     0.532        0.974   
5             saga         1      0.592      0.594     0.532        0.974   

   recall_1  precision_1  
0     0.608        0.045  
1     0.609        0.045  
2     0.608        0.045  
3     0.609        0.045  
4     0.609        0.045  
5     0.609        0.045

##### <span style="color:MediumSlateBlue">Подбор гиперпараметров модели</span>

In [1632]:
# для выбора sceler преобразвания на понадобится словарь
dict_scalers ={
    'MinMaxScaler':MinMaxScaler(),
    'RobustScaler':RobustScaler(),
    'StandardScaler':StandardScaler(),
}
# определим пространство признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'service'
count_features = dict_spaces[feature_space]

# настроим оптимизацию гипер параметров
def optuna_lg(trial):
  # задаем пространства поиска гиперпараметров
  C = trial.suggest_float('C',0.01,1)
  solver = trial.suggest_categorical('solver', ['lbfgs', 'liblinear', 'newton-cg', 'newton-cholesky'])
  class_0_weight = trial.suggest_float('class_0_weight',0.01,1)
  class_1_weight = trial.suggest_float('class_1_weight',0.01,1)
  n_last = trial.suggest_int('n_last', 10, 25,step = 1)
  class_1_percent = trial.suggest_float('class_1_percent',0.01,1)
  scaler = trial.suggest_categorical('scaler', ['MinMaxScaler', 'RobustScaler','StandardScaler'])
  random_state = trial.suggest_int('random_state', 1, 1000000)

  # создаем модель
  optuna_log_reg = linear_model.LogisticRegression(
      solver=solver,
      C=C,
      class_weight={0:class_0_weight,1:class_1_weight},
      random_state=random_state,
      max_iter=10000)

  # с помощью функции features_from_transform_data_torow извлечем  
  # из данных transform_data_torow
  # признаки сооствествующие n_last последним клиенским операциям
  list_n_last_features = features_from_transform_data_torow(n_last,count_features,25)

  # обьявим scaler
  scaler = dict_scalers[scaler]

  # загружаем обучующие наборы
  X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
  y_train_pd = pd.read_csv('target/target_train.csv')

  # поготовим данные y_train_pd к работе с функцией class_1_percent_samples
  y_train_pd.set_index('id',drop=False,inplace=True)

  # подготовим данные для обучения модели
  # с помощью функции class_1_percent_samples зададим долю 
  # класса 1
  list_c1_percent_id = class_1_percent_samples(y_train_pd,class_1_percent,random_state=random_state)[:1000000]

  # сформируем данные для обучения базовой модели
  X_train_s_balanced = scaler.fit_transform(np.array(X_train_pd.loc[list_c1_percent_id])[:,list_n_last_features])
  y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

  # освободим память от "тяжелых" и ненужных файлов
  del X_train_pd, y_train_pd
  gc.collect()

  # я не воспользовался параметром timeout метода optimize потому, что  
  # optimize отставливает поиск параметров, если время обучения 
  # превышает timeout. Мне нужно чтобы поиск параметров продолжился.
  try:
    # для модуля func_time_out упакуем обучение модели в функцию try_func
    def try_func():
            return optuna_log_reg.fit(X_train_s_balanced, y_train_balanced)
    # обучаем модель с ограничением по времени 10 минут (600 секунд)
    optuna_log_reg = func_timeout.func_timeout(600, try_func)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train_s_balanced,y_train_balanced
    gc.collect()

    # подгружаем данные для тестирования
    X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()[:,list_n_last_features]
    y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
    X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()[:,list_n_last_features]
    y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

    # сформируем данные для проверки модели
    X_train_s = scaler.transform(X_train)
    X_valid_s = scaler.transform(X_valid)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train, X_valid
    gc.collect()

    # делаем предсказание на обучающем и валидационном наборе и считаем метрики
    roc_train = metrics.roc_auc_score(y_train, optuna_log_reg.predict_proba(X_train_s)[:,1])
    roc_valid = metrics.roc_auc_score(y_valid, optuna_log_reg.predict_proba(X_valid_s)[:,1])
    f1_score = metrics.f1_score(y_valid, optuna_log_reg.predict(X_valid_s))
    recall_1 = metrics.recall_score(y_valid, optuna_log_reg.predict(X_valid_s),average=None,zero_division=0)[1]
    precision_1 = metrics.precision_score(y_valid, optuna_log_reg.predict(X_valid_s),average=None,zero_division=0)[1]

    del X_train_s, X_valid_s, y_train, y_valid
    gc.collect()

  except func_timeout.FunctionTimedOut:
    # освободим память от "тяжелых" и ненужных файлов
    del X_train_s_balanced, y_train_balanced
    gc.collect()

    # обьявим метрики пустыми значениями
    roc_train = 0
    roc_valid = 0
    f1_score = 0
    recall_1 = 0
    precision_1 = 0
    pass

  return roc_train, roc_valid, f1_score, recall_1, precision_1

In [1633]:
# cоздаем объект исследования
# чтобы модель не переобучалась минимизируем roc_train 
# и максимизируем roc_valid
optuna_study_lg = optuna.create_study(study_name='LogisticRegression_'+feature_space+'_torow', 
                               directions=['maximize','maximize','maximize','maximize','maximize'], 
                               sampler=optuna.samplers.TPESampler(),
                               pruner='Hyperband',
                               storage='sqlite:///optuna_studies.db',
                               load_if_exists=True)
# на случай удаления 
# optuna.delete_study(study_name='LogisticRegression_'+feature_space+'_torow', storage='sqlite:///optuna_studies.db')

[I 2025-04-19 14:27:59,894] Using an existing study with name 'LogisticRegression_service_torow' instead of creating a new one.


In [526]:
# ищем лучшую комбинацию гиперпараметров n_trials раз
optuna_study_lg.optimize(optuna_lg, n_trials=300)

[I 2025-04-17 18:23:04,312] Trial 0 finished with values: [0.5743571115029021, 0.5746348043888928, 0.06792370809107211, 0.9988014382740711, 0.035157293732157674] and parameters: {'C': 0.5903311071802956, 'solver': 'newton-cholesky', 'class_0_weight': 0.24357160267445235, 'class_1_weight': 0.05255102541851544, 'n_last': 19, 'class_1_percent': 0.970387928444233, 'scaler': 'StandardScaler', 'random_state': 977173}.
[I 2025-04-17 18:23:08,091] Trial 1 finished with values: [0.5937679291584637, 0.5953894063359731, 0.07394090719933416, 0.8873351977626848, 0.0385777808656986] and parameters: {'C': 0.6111980653672742, 'solver': 'lbfgs', 'class_0_weight': 0.8687436582663074, 'class_1_weight': 0.5480214167355816, 'n_last': 22, 'class_1_percent': 0.6900340897853253, 'scaler': 'RobustScaler', 'random_state': 347726}.
[I 2025-04-17 18:23:11,967] Trial 2 finished with values: [0.5956926986349687, 0.5982973485768522, 0.06867095629021522, 0.98921294446664, 0.035570113060092806] and parameters: {'C': 0

In [1634]:
# из полученного результат соврмируем Data Frame
optuna_study_lg_pd = optuna_study_lg.trials_dataframe().dropna()
# переименуем столбы
optuna_study_lg_pd.rename(columns={
    'values_0': 'roc_train',
    'values_1': 'roc_valid',
    'values_2': 'f1_score',
    'values_3': 'recall_1',
    'values_4': 'precision_1'
},inplace=True)
# Выделим время потраченное на обучение модели
optuna_study_lg_pd.head(5)

number  roc_train  roc_valid  f1_score  recall_1  precision_1  \
0       0   0.574357   0.574635  0.067924  0.998801     0.035157   
1       1   0.593768   0.595389  0.073941  0.887335     0.038578   
2       2   0.595693   0.598297  0.068671  0.989213     0.035570   
3       3   0.596047   0.598851  0.089659  0.467439     0.049585   
4       4   0.590296   0.592132  0.067895  1.000000     0.035140   

              datetime_start          datetime_complete  \
0 2025-04-17 18:23:00.516991 2025-04-17 18:23:04.309118   
1 2025-04-17 18:23:04.315204 2025-04-17 18:23:08.087205   
2 2025-04-17 18:23:08.094088 2025-04-17 18:23:11.964365   
3 2025-04-17 18:23:11.970038 2025-04-17 18:23:15.589454   
4 2025-04-17 18:23:15.595603 2025-04-17 18:23:19.007005   

                duration  params_C  params_class_0_weight  \
0 0 days 00:00:03.792127  0.590331               0.243572   
1 0 days 00:00:03.772001  0.611198               0.868744   
2 0 days 00:00:03.870277  0.847434               0.022405   
3 0 days 00:00:03.619416  0.345003               0.403761   
4 0 days 00:00:03.411402  0.986567               0.787402   

   params_class_1_percent  params_class_1_weight  params_n_last  \
0                0.970388               0.052551             19   
1                0.690034               0.548021             22   
2                0.216033               0.195720             13   
3                0.309170               0.816401             13   
4                0.883570               0.839922             11   

   params_random_state   params_scaler    params_solver     state  
0               977173  StandardScaler  newton-cholesky  COMPLETE  
1               347726    RobustScaler            lbfgs  COMPLETE  
2               401128    RobustScaler        newton-cg  COMPLETE  
3               354215    MinMaxScaler        liblinear  COMPLETE  
4               407914    RobustScaler        liblinear  COMPLETE

In [528]:
# покаждем статистику обучения
print('Максимальное значение метрики ROC AUC на валидационном наборе:',round(optuna_study_lg_pd['roc_valid'].max(),3))
print('Среднее значение метрики ROC AUC на валидационном наборе:',round(optuna_study_lg_pd['roc_valid'].mean(),3))
print('Максимальное значение метрики f1_score на валидационном наборе:',round(optuna_study_lg_pd['f1_score'].max(),3))
print('Среднее значение метрики f1_score на валидационном наборе:',round(optuna_study_lg_pd['f1_score'].mean(),3))
print('Максимальное значение метрики recall_1 на валидационном наборе:',round(optuna_study_lg_pd['recall_1'].max(),3))
print('Среднее значение метрики recall_1 на валидационном наборе:',round(optuna_study_lg_pd['recall_1'].mean(),3))
print('Максимальное значение метрики precision_1 на валидационном наборе:',round(optuna_study_lg_pd['precision_1'].max(),3))
print('Среднее значение метрики precision_1 на валидационном наборе:',round(optuna_study_lg_pd['precision_1'].mean(),3))

Максимальное значение метрики ROC AUC на валидационном наборе: 0.601
Среднее значение метрики ROC AUC на валидационном наборе: 0.597
Максимальное значение метрики f1_score на валидационном наборе: 0.092
Среднее значение метрики f1_score на валидационном наборе: 0.062
Максимальное значение метрики recall_1 на валидационном наборе: 1.0
Среднее значение метрики recall_1 на валидационном наборе: 0.469
Максимальное значение метрики precision_1 на валидационном наборе: 0.154
Среднее значение метрики precision_1 на валидационном наборе: 0.046


In [1636]:
# Визуализируем метрики полученные при optuna оптимизации
fig = px.scatter(
    data_frame=optuna_study_lg_pd[
                                (optuna_study_lg_pd['roc_valid']>0.999*optuna_study_lg_pd['roc_valid'].max())],
    x='number', #ось абсцисс
    y=['roc_train','roc_valid','recall_1','precision_1'], #ось ординат
)
fig.update_layout(
    title ={
        'text':'Зависимость качества модели от trials optuna', # Имя рабочей плоскости
        'font':{'size':35,'family':"Times New Roman"}, # размер и стиль написания имени рабочей плоскости
        'x':0.5, # Смешение имени по оси "x" на половину рабочей плоскости
        },
    height =800,# Высота рабочей плоскости
    width = 1350, # Ширина рабочей плоскости
    bargap=0.2, # Добавил расстояния между столбами гистограммы
    xaxis_title='trials optuna',
    yaxis_title='Величина метрики')
fig.update_xaxes(showspikes=True)
fig.update_yaxes(showspikes=True)

fig.show()

<span style="color:Blue">

Вывод:  

Их всех выбираем точку $number =171$.   
В этой точке одно из самых больших значений $ROC AUC$.  
Посмотрим каким значениям гиперпараметров соотвествует выбранная точка.

In [1637]:
# определим номер лучшге варианта
best_optuna_number = 171

# сформируем словарь лучших гипирпарметров RandomForestClassifier
best_param_lr_torow = {
    'C' : round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_C'].iloc[0],3),
    'class_weight' : {0:round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_class_0_weight'].iloc[0],3),
                      1:round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_class_1_weight'].iloc[0],3)},
    }
# создадим перменные
best_n_last = int(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_n_last'].iloc[0])
best_scaler = optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_scaler'].iloc[0]
best_class_1_percent = optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_class_1_percent'].iloc[0]
best_random_state = int(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_random_state'].iloc[0])
# Выведем принятые наилучшие праметры
print('best C:',best_param_lr_torow['C'])
print('best class 0 weight:',best_param_lr_torow['class_weight'][0])
print('best class 1 weight:',best_param_lr_torow['class_weight'][1])

print('best class 1 percent:',round(best_class_1_percent,3))
print('best scaler:',best_scaler)
print('best n_last:',round(best_n_last,3))
print('best best random state:',best_random_state)
print('time for best train:',round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['duration'].iloc[0].seconds/60),'minutes')

print()
print('ROC AUC на обучающем наборе:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['roc_train'].iloc[0],3))
print('ROC AUC на валидационном наборе:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['roc_valid'].iloc[0],3))
print('precision класса 1:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['precision_1'].iloc[0],3))
print('recall класса 1:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['recall_1'].iloc[0],3))

best C: 0.608
best class 0 weight: 0.505
best class 1 weight: 0.627
best class 1 percent: 0.385
best scaler: MinMaxScaler
best n_last: 14
best best random state: 695397
time for best train: 0 minutes

ROC AUC на обучающем наборе: 0.596
ROC AUC на валидационном наборе: 0.601
precision класса 1: 0.056
recall класса 1: 0.259


##### <span style="color:MediumSlateBlue">Обучение модели с лучшими параметрами</span>

In [1638]:
# для выбора sceler преобразвания на понадобится словарь
dict_scalers ={
    'MinMaxScaler':MinMaxScaler(),
    'RobustScaler':RobustScaler(),
    'StandardScaler':StandardScaler(),
}

# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'service'
count_features = dict_spaces[feature_space]

# с помощью функции features_from_transform_data_torow извлечем  
# из данных transform_data_torow_25
# признаки сооствествующие n_last последним клиенским операциям
list_n_last_features = features_from_transform_data_torow(best_n_last,count_features,25)

# обьявим scaler
scaler = dict_scalers[best_scaler]

# загружаем обучующие наборы
X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)

# подготовим данные для обучения модели
# с помощью функции class_1_percent_samples зададим долю 
# класса 1
list_c1_percent_id = class_1_percent_samples(y_train_pd,best_class_1_percent,random_state=best_random_state)[:1000000]

# сформируем данные для обучения базовой модели
X_train_s_balanced = scaler.fit_transform(np.array(X_train_pd.loc[list_c1_percent_id])[:,list_n_last_features])
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

# освободим память от "тяжелых" и ненужных файлов
del X_train_pd, y_train_pd
gc.collect()


# обучаем модель LogisticRegression с наилучшеми параметрами
logistic_regression = linear_model.LogisticRegression(
        **best_param_lr_torow,
        random_state=best_random_state,
        max_iter=10000)
logistic_regression.fit(X_train_s_balanced,y_train_balanced)

# удаляем крупные файлы чтобы высвободить память 
del X_train_s_balanced,y_train_balanced
gc.collect()

# подгружаем данные для тестирования
X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()[:,list_n_last_features]
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()[:,list_n_last_features]
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()
    
# сформируем данные для проверки модели
X_train_s = scaler.transform(X_train)
X_valid_s = scaler.transform(X_valid)

# удаляем крупные файлы чтобы высвободить память 
del X_train, X_valid
gc.collect()

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_lr_pred_proba = logistic_regression.predict_proba(X_train_s)[:,1]
y_valid_lr_pred_proba = logistic_regression.predict_proba(X_valid_s)[:,1]

# Делаем предсказание для валидационной выборки
y_valid_lr_pred = logistic_regression.predict(X_valid_s)

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_lr_pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_lr_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_lr_pred,zero_division=0))

# time: 2m 40s

ROC AUC на обучающем наборе 0.596
ROC AUC на валидационном наборе 0.601
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.97      0.84      0.90     68747
           1       0.06      0.26      0.09      2503

    accuracy                           0.82     71250
   macro avg       0.51      0.55      0.50     71250
weighted avg       0.94      0.82      0.87     71250



#### <span style="color:MediumBlue">Построение модели Random Forest Classifier</span>

##### <span style="color:MediumSlateBlue">Формирование данных для обучения</span>

Анализ исходных данных, в частности target, показал что представленные данные   
имееют перекос: 96% клиентов у которых не случился дефолт (flag = 0),    
против 4 % - для которых произошел дефолт (flag = 1).  
С помощью функции class_1_percent_samples, сформируем сбаланисрованную выборку  
для обучения моделей.
За основу сбалансировных данных возьмем данные клиентов с дефолтом  
и к ним будем добирать необходимое количество клиентов до сбалансированности. 


Функция class_1_percent_samples принемает две переменные:
- target_data - массив с id и целевой переменной
- class_1_percent - процент класса 1 в результирующем массиве

In [544]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'service'
count_features = dict_spaces[feature_space]

In [545]:
# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

In [546]:
# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)
y_train_pd.head(4)

id  flag
id                    
1825800  1825800     0
2166483  2166483     0
2534345  2534345     0
1803283  1803283     0

In [547]:
# взглянем на сблансиорованность данных в y_train
y_train_pd['flag'].value_counts(normalize=True)

flag
0    0.964242
1    0.035758
Name: proportion, dtype: float64

In [548]:
# сбалансируем данные в y_train_pd
list_c1_percent_id = class_1_percent_samples(y_train_pd,0.5)
# list_c1_percent_features - список 'id' из y_train_pd соотвествующих  
# заданному проценту класса 1
len(list_c1_percent_id)

45860

In [549]:
# проверим сбалансированность полученного y_train
y_train_pd.loc[list_c1_percent_id]['flag'].value_counts(normalize=True)

flag
1    0.5
0    0.5
Name: proportion, dtype: float64

*transform_data_torow*, показываеются последние N операций клиента.  
В данных в *date_torow*, собраны последние 25 операций клиентов.

Предварительный анализ показывает, что медиальное значение количества клиентских  
операций равно 7. Поэтому, для начала, будем показывать моделе $n_{last} = 7$   
последних клиентских операций.

Для извлечения из *transform_data_torow_25* необходимого количества последних клиенских  
операций ($n_{last}$) используем функцию features_from_transform_data_torow.

Функция features_from_transform_data_torow примает следующие аргументы:
- $n_{last} = 7$ - необходимое количество последних клиентских операций; 
- $n_{groups} = 8$ - количество признаков в $date$ $features$;
- $N_{last} = 25$ - количество $n_{last}$ операций, показанных в transform_data_torow_25


In [550]:
# с помощью функции features_from_transform_data_torow извлечем  
# из данных transform_data_torow_25
# признаки сооствествующие 7 последним клиенским операциям
list_n_last_features = features_from_transform_data_torow(7,count_features,25)

In [551]:
# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']
# сформируем данные для проверики модели
X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

In [552]:
# посмотрим на структуру данных в X_train_balanced
X_train_balanced.head(2)

f1  f2  f3  f4  f5  f6  f7  f8  f9  f10  ...  f91  f92  f93  f94  \
id                                                ...                       
2335465   1   1   1   1   1   1   1   1   1    1  ...    1    1    0    0   
390270    1   1   1   1   1   1   0   0   0    0  ...    0    0    0    0   

         f95  f96  f97  f98  f99  f100  
id                                      
2335465    0    0    0    0    0     0  
390270     0    0    0    0    0     0  

[2 rows x 100 columns]

In [553]:
# посмотрим на структуру данных в y_train_balanced
y_train_balanced.head(2)

id
2335465    1
390270     1
Name: flag, dtype: int64

In [554]:
# проверим что выборки действительно совпадают по id
X_train_balanced.index.to_list() == y_train_balanced.index.to_list()

True

##### <span style="color:MediumSlateBlue">Baseline обучение модели RandomForestClassifier</span>

In [555]:
# обучаем модель логистической регрессии
# чтобы модель пыталась найти связь во всех признаках
random_forest = RandomForestClassifier(random_state=42, n_jobs=-1)
random_forest.fit(np.array(X_train_balanced)[:,list_n_last_features],np.array(y_train_balanced))

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_rf__pred_proba = random_forest.predict_proba(X_train[:,list_n_last_features])[:,1]
y_valid_rf_pred_proba = random_forest.predict_proba(X_valid[:,list_n_last_features])[:,1]

# Делаем предсказание для валидационной выборки
y_valid_rf_pred = random_forest.predict(X_valid[:,list_n_last_features])

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_rf__pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_rf_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_rf_pred))

# time: 2m 5s

ROC AUC на обучающем наборе 0.787
ROC AUC на валидационном наборе 0.585
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.97      0.53      0.69     68747
           1       0.04      0.60      0.08      2503

    accuracy                           0.54     71250
   macro avg       0.51      0.57      0.39     71250
weighted avg       0.94      0.54      0.67     71250



##### <span style="color:MediumSlateBlue">Подбор гиперпараметров модели</span>

In [1639]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'service'
count_features = dict_spaces[feature_space]

# настроим оптимизацию гипер параметров
def optuna_rf(trial):
  # задаем пространства поиска гиперпараметров
  # задаем пространства поиска гиперпараметров
  n_estimators = trial.suggest_int('n_estimators', 50, 150,step = 5)
  criterion = trial.suggest_categorical('criterion',['gini', 'entropy', 'log_loss'])
  max_depth = trial.suggest_int('max_depth', 9, 20,step = 1)
  min_samples_split = trial.suggest_int('min_samples_split', 5, 15,step = 1)
  min_samples_leaf = trial.suggest_int('min_samples_leaf', 5, 25,step = 1)
  max_features = trial.suggest_float('max_features',0.1,1)
  max_samples = trial.suggest_float('max_samples',0.1,1)
  class_0_weight = trial.suggest_float('class_0_weight',0.01,1)
  class_1_weight = trial.suggest_float('class_1_weight',0.01,1)
  n_last = trial.suggest_int('n_last', 5, 25,step = 1)
  class_1_percent = trial.suggest_float('class_1_percent',0.01,1)
  random_state = trial.suggest_int('random_state', 1, 1000000)


  # создаем модель
  optuna_random_forest = RandomForestClassifier(
      n_estimators = n_estimators, 
      criterion = criterion,
      max_depth = max_depth,
      min_samples_split = min_samples_split,  
      min_samples_leaf = min_samples_leaf,
      max_features=max_features,
      max_samples=max_samples,
      class_weight={0:class_0_weight,1:class_1_weight},
      n_jobs=-1,
      random_state=random_state)

  # с помощью функции features_from_transform_data_torow извлечем  
  # из данных transform_data_torow
  # признаки сооствествующие n_last последним клиенским операциям
  list_n_last_features = features_from_transform_data_torow(n_last,count_features,25)

  # загружаем обучующие наборы
  X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
  y_train_pd = pd.read_csv('target/target_train.csv')

  # поготовим данные y_train_pd к работе с функцией class_1_percent_samples
  y_train_pd.set_index('id',drop=False,inplace=True)

  # подготовим данные для обучения модели
  # с помощью функции class_1_percent_samples зададим долю 
  # класса 1
  list_c1_percent_id = class_1_percent_samples(y_train_pd,class_1_percent,random_state=random_state)[:1000000]

  # сформируем данные для обучения базовой модели
  X_train_balanced = np.array(X_train_pd.loc[list_c1_percent_id])[:,list_n_last_features]
  y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

  # освободим память от "тяжелых" и ненужных файлов
  del X_train_pd, y_train_pd
  gc.collect()

  # я не воспользовался параметром timeout метода optimize потому, что  
  # optimize отставливает поиск параметров, если время обучения 
  # превышает timeout. Мне нужно чтобы поиск параметров продолжился.
  try:
    # для модуля func_time_out упакуем обучение модели в функцию try_func
    def try_func():
            return optuna_random_forest.fit(X_train_balanced,y_train_balanced)
    # обучаем модель с ограничением по времени 10 минут (600 секунд)
    optuna_random_forest = func_timeout.func_timeout(600, try_func)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train_balanced, y_train_balanced
    gc.collect()

    # подгружаем данные для тестирования
    X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()[:,list_n_last_features]
    y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
    X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()[:,list_n_last_features]
    y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

    # делаем предсказание на обучающем и валидационном наборе и считаем метрики
    roc_train = metrics.roc_auc_score(y_train, optuna_random_forest.predict_proba(X_train)[:,1])
    roc_valid = metrics.roc_auc_score(y_valid, optuna_random_forest.predict_proba(X_valid)[:,1])
    f1_score = metrics.f1_score(y_valid, optuna_random_forest.predict(X_valid))
    recall_1 = metrics.recall_score(y_valid, optuna_random_forest.predict(X_valid),average=None,zero_division=0)[1]
    precision_1 = metrics.precision_score(y_valid, optuna_random_forest.predict(X_valid),average=None,zero_division=0)[1]

    # удаляем крупные файлы чтобы высвободить память 
    del X_train, X_valid, y_train, y_valid 
    gc.collect()

  except func_timeout.FunctionTimedOut:
    # освободим память от "тяжелых" и ненужных файлов
    del X_train_balanced, y_train_balanced
    gc.collect()

    # обьявим метрики пустыми значениями
    roc_train = 0
    roc_valid = 0
    f1_score = 0
    recall_1 = 0
    precision_1 = 0
    pass

  return roc_train, roc_valid, f1_score, recall_1, precision_1

In [1640]:
# так как Random Forest склонен к переобучению 
# попробуем направить optimize в сторону уменьшения roc_train
# cоздаем объект исследования
optuna_study_rf = optuna.create_study(study_name='RandomForestClassifier_'+feature_space+'_torow', 
                               directions=['minimize','maximize','maximize','maximize','maximize'], 
                               sampler=optuna.samplers.TPESampler(),
                               pruner='Hyperband',
                               storage='sqlite:///optuna_studies.db',
                               load_if_exists=True)
# на случай удаления 
# optuna.delete_study(study_name='RandomForestClassifier_'+feature_space+'_torow', storage='sqlite:///optuna_studies.db')

[I 2025-04-19 14:29:39,349] Using an existing study with name 'RandomForestClassifier_service_torow' instead of creating a new one.


In [558]:
# ищем лучшую комбинацию гиперпараметров n_trials раз
optuna_study_rf.optimize(optuna_rf, n_trials=300)

[I 2025-04-17 18:47:59,859] Trial 0 finished with values: [0.6495417009849064, 0.6293342951147903, 0.06823179142595703, 0.9980023971234518, 0.035323397154896914] and parameters: {'n_estimators': 105, 'criterion': 'gini', 'max_depth': 12, 'min_samples_split': 14, 'min_samples_leaf': 6, 'max_features': 0.2784016134919776, 'max_samples': 0.6905995114713662, 'class_0_weight': 0.346378113143684, 'class_1_weight': 0.9772173782608208, 'n_last': 22, 'class_1_percent': 0.6082498192756411, 'random_state': 747494}.
[I 2025-04-17 18:48:03,393] Trial 1 finished with values: [0.6412976303289524, 0.6267394715385424, 0.06787520507640367, 1.0, 0.03512982456140351] and parameters: {'n_estimators': 60, 'criterion': 'gini', 'max_depth': 16, 'min_samples_split': 13, 'min_samples_leaf': 10, 'max_features': 0.10989683559295782, 'max_samples': 0.474158407823794, 'class_0_weight': 0.29821002850111833, 'class_1_weight': 0.7320109269897684, 'n_last': 16, 'class_1_percent': 0.7255983165204594, 'random_state': 700

In [1641]:
# из полученного результат соврмируем Data Frame
optuna_study_rf_pd = optuna_study_rf.trials_dataframe().dropna()
# переименуем столбы
optuna_study_rf_pd.rename(columns={
    'values_0': 'roc_train',
    'values_1': 'roc_valid',
    'values_2': 'f1_score',
    'values_3': 'recall_1',
    'values_4': 'precision_1'
},inplace=True)
optuna_study_rf_pd.sort_values(by='precision_1').drop(['datetime_start','datetime_complete','duration'],axis=1)

number  roc_train  roc_valid  f1_score  recall_1  precision_1  \
89       89   0.701723   0.628993  0.000000  0.000000     0.000000   
195     195   0.636625   0.627732  0.000000  0.000000     0.000000   
215     215   0.638090   0.628879  0.000000  0.000000     0.000000   
219     219   0.690734   0.630516  0.000000  0.000000     0.000000   
181     181   0.635286   0.627630  0.000000  0.000000     0.000000   
..      ...        ...        ...       ...       ...          ...   
165     165   0.648996   0.625799  0.013219  0.006792     0.246377   
208     208   0.632998   0.628696  0.013224  0.006792     0.250000   
268     268   0.634984   0.626559  0.001594  0.000799     0.285714   
270     270   0.641214   0.630659  0.002388  0.001199     0.300000   
298     298   0.628413   0.623863  0.001595  0.000799     0.400000   

     params_class_0_weight  params_class_1_percent  params_class_1_weight  \
89                0.588029                0.052639               0.206481   
195               0.640738                0.516960               0.011526   
215               0.656402                0.548792               0.027400   
219               0.579642                0.040939               0.122269   
181               0.589848                0.543021               0.015737   
..                     ...                     ...                    ...   
165               0.695395                0.677424               0.059548   
208               0.215407                0.571219               0.052943   
268               0.511008                0.553443               0.051903   
270               0.578249                0.110801               0.538817   
298               0.571482                0.559833               0.034464   

    params_criterion  params_max_depth  params_max_features  \
89           entropy                18             0.542284   
195          entropy                15             0.737309   
215          entropy                12             0.254725   
219          entropy                20             0.204461   
181          entropy                10             0.288778   
..               ...               ...                  ...   
165             gini                20             0.266927   
208          entropy                15             0.178251   
268          entropy                 9             0.278952   
270          entropy                 9             0.327345   
298         log_loss                 9             0.254454   

     params_max_samples  params_min_samples_leaf  params_min_samples_split  \
89             0.139952                        6                         9   
195            0.218363                       19                         8   
215            0.227798                       20                         9   
219            0.153925                        8                         9   
181            0.201050                       21                         9   
..                  ...                      ...                       ...   
165            0.831362                       25                         6   
208            0.171091                       19                        10   
268            0.741274                       21                        11   
270            0.720204                        7                        12   
298            0.243214                        8                        10   

     params_n_estimators  params_n_last  params_random_state     state  
89                    60             23               784864  COMPLETE  
195                  130              5               529658  COMPLETE  
215                  115             12               740196  COMPLETE  
219                   65             10               730924  COMPLETE  
181                   75             15               487161  COMPLETE  
..                   ...            ...                  ...       ...  
165                  145          

In [560]:
# покаждем статистику обучения
print('Максимальное значение метрики ROC AUC на валидационном наборе:',round(optuna_study_rf_pd['roc_valid'].max(),3))
print('Среднее значение метрики ROC AUC на валидационном наборе:',round(optuna_study_rf_pd['roc_valid'].mean(),3))
print('Максимальное значение метрики f1_score на валидационном наборе:',round(optuna_study_rf_pd['f1_score'].max(),3))
print('Среднее значение метрики f1_score на валидационном наборе:',round(optuna_study_rf_pd['f1_score'].mean(),3))
print('Максимальное значение метрики recall_1 на валидационном наборе:',round(optuna_study_rf_pd['recall_1'].max(),3))
print('Среднее значение метрики recall_1 на валидационном наборе:',round(optuna_study_rf_pd['recall_1'].mean(),3))
print('Максимальное значение метрики precision_1 на валидационном наборе:',round(optuna_study_rf_pd['precision_1'].max(),3))
print('Среднее значение метрики precision_1 на валидационном наборе:',round(optuna_study_rf_pd['precision_1'].mean(),3))

Максимальное значение метрики ROC AUC на валидационном наборе: 0.635
Среднее значение метрики ROC AUC на валидационном наборе: 0.62
Максимальное значение метрики f1_score на валидационном наборе: 0.112
Среднее значение метрики f1_score на валидационном наборе: 0.067
Максимальное значение метрики recall_1 на валидационном наборе: 1.0
Среднее значение метрики recall_1 на валидационном наборе: 0.555
Максимальное значение метрики precision_1 на валидационном наборе: 0.4
Среднее значение метрики precision_1 на валидационном наборе: 0.061


In [1652]:
# Построим зависимость метрик качества модели от number

fig = px.scatter(
    data_frame=optuna_study_rf_pd[(optuna_study_rf_pd['roc_valid']>=0.9999*optuna_study_rf_pd['roc_valid'].max())],
    x='number', #ось абсцисс
    y=['roc_valid','roc_train','precision_1','recall_1'], #ось ординат
)
fig.update_layout(
    title ={
        'text':'Зависимость метрик качества модели от number', # Имя рабочей плоскости
        'font':{'size':35,'family':"Times New Roman"}, # размер и стиль написания имени рабочей плоскости
        'x':0.5, # Смешение имени по оси "x" на половину рабочей плоскости
        },
    height =800,# Высота рабочей плоскости
    width = 1350, # Ширина рабочей плоскости
    bargap=0.2, # Добавил расстояния между столбами гистограммы
    xaxis_title='Величина метрики ROC Valid',
    yaxis_title='Величина параметра')
fig.update_xaxes(showspikes=True)
fig.update_yaxes(showspikes=True)

fig.show()

<span style="color:Blue">

Вывод:  

Их всех выбираем точку $number =147$.   
В этой точке оптимальные значения метрик $recall_1$ и $precision_1$, а  
также относительно высокая метрика $ROC AUC$.   
Посмотрим каким значениям гиперпараметров соотвествует выбраннаяточка.

In [1653]:
# определим номер лучшге варианта
best_optuna_number = 147

# сформируем словарь лучших гипирпарметров RandomForestClassifier
best_param_rf = {
    'n_estimators' : int(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_n_estimators'].iloc[0]),
    'criterion': optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_criterion'].iloc[0],
    'max_depth' : optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_max_depth'].iloc[0],
    'min_samples_split': optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_min_samples_split'].iloc[0],
    'min_samples_leaf' : optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_min_samples_leaf'].iloc[0],
    'max_features': optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_max_features'].iloc[0],
    'max_samples' : optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_max_samples'].iloc[0],
    'class_weight' : {0:optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_class_0_weight'].iloc[0],
                      1:optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_class_1_weight'].iloc[0]}
    }
# определим перменные для лучших значений параметров
best_n_last = optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_n_last'].iloc[0]
best_class_1_percent = optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_class_1_percent'].iloc[0]
best_random_state = optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_random_state'].iloc[0]


# Выведем принятые наилучшие праметры
print('best n estimators:',best_param_rf['n_estimators'])
print('best criterion:',best_param_rf['criterion'])
print('best max depth:',best_param_rf['max_depth'])
print('best min samples split:',best_param_rf['min_samples_split'])
print('best min samples leaf:',best_param_rf['min_samples_leaf'])
print('best max features(%):',round(best_param_rf['max_features'],3))
print('best max samples(%):',round(best_param_rf['max_samples'],3))
print('best class 0 weight:',round(best_param_rf['class_weight'][0],3))
print('best class 1 weight:',round(best_param_rf['class_weight'][1],3))

print('best class 1 percent:',round(best_class_1_percent,3))
print('best n last:',best_n_last)
print('best random state:',best_random_state)
print('time for best train:',round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['duration'].iloc[0].seconds/60),'minutes')

print()
print('ROC AUC на обучающем наборе:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['roc_train'].iloc[0],3))
print('ROC AUC на валидационном наборе:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['roc_valid'].iloc[0],3))
print('precision класса 1:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['precision_1'].iloc[0],3))
print('recall класса 1:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['recall_1'].iloc[0],3))

best n estimators: 130
best criterion: gini
best max depth: 17
best min samples split: 15
best min samples leaf: 6
best max features(%): 0.145
best max samples(%): 0.535
best class 0 weight: 0.625
best class 1 weight: 0.268
best class 1 percent: 0.268
best n last: 17
best random state: 831219
time for best train: 0 minutes

ROC AUC на обучающем наборе: 0.672
ROC AUC на валидационном наборе: 0.635
precision класса 1: 0.235
recall класса 1: 0.002


##### <span style="color:MediumSlateBlue">Обучение модели с лучшими параметрами</span>

In [1654]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'service'
count_features = dict_spaces[feature_space]

# с помощью функции features_from_transform_data_torow извлечем  
# из данных transform_data_torow
# признаки сооствествующие n_last последним клиенским операциям
list_n_last_features = features_from_transform_data_torow(best_n_last,count_features,25)

# загружаем обучующие наборы
X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)

# подготовим данные для обучения модели
# с помощью функции class_1_percent_samples зададим долю 
# класса 1
list_c1_percent_id = class_1_percent_samples(y_train_pd,best_class_1_percent,random_state=best_random_state)[:1000000]

# сформируем данные для обучения базовой модели
X_train_balanced = np.array(X_train_pd.loc[list_c1_percent_id])[:,list_n_last_features]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

# освободим память от "тяжелых" и ненужных файлов
del X_train_pd, y_train_pd
gc.collect()

# обучаем модель RandomForestClassifier с наилучшеми параметрами
random_forest = RandomForestClassifier(
        **best_param_rf,
        n_jobs=-1,
        random_state=best_random_state)
random_forest.fit(X_train_balanced, y_train_balanced)

# освободим память от "тяжелых" и ненужных файлов
del X_train_balanced, y_train_balanced
gc.collect()


# подгружаем данные для тестирования
X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()[:,list_n_last_features]
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()[:,list_n_last_features]
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_rf__pred_proba = random_forest.predict_proba(X_train)[:,1]
y_valid_rf_pred_proba = random_forest.predict_proba(X_valid)[:,1]

# Делаем предсказание для валидационной выборки
y_valid_rf_pred = random_forest.predict(X_valid)

# удаляем крупные файлы чтобы высвободить память 
del X_train, X_valid
gc.collect()

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_rf__pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_rf_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_rf_pred,zero_division=0))

# time: 2m 10s

ROC AUC на обучающем наборе 0.672
ROC AUC на валидационном наборе 0.635
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.96      1.00      0.98     68747
           1       0.24      0.00      0.00      2503

    accuracy                           0.96     71250
   macro avg       0.60      0.50      0.49     71250
weighted avg       0.94      0.96      0.95     71250



#### <span style="color:MediumBlue">Построение модели Gradient Boosting Classifier</span>

##### <span style="color:MediumSlateBlue">Формирование данных для обучения</span>

Анализ исходных данных, в частности target, показал что представленные данные   
имееют перекос: 96% клиентов у которых не случился дефолт (flag = 0),    
против 4 % - для которых произошел дефолт (flag = 1).  
С помощью функции class_1_percent_samples, сформируем сбаланисрованную выборку  
для обучения моделей.
За основу сбалансировных данных возьмем данные клиентов с дефолтом  
и к ним будем добирать необходимое количество клиентов до сбалансированности. 


Функция class_1_percent_samples принемает две переменные:
- target_data - массив с id и целевой переменной
- class_1_percent - процент класса 1 в результирующем массиве

In [576]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'service'
count_features = dict_spaces[feature_space]

In [577]:
# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

In [578]:
# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)
y_train_pd.head(4)

id  flag
id                    
1825800  1825800     0
2166483  2166483     0
2534345  2534345     0
1803283  1803283     0

In [579]:
# взглянем на сблансиорованность данных в y_train
y_train_pd['flag'].value_counts(normalize=True)

flag
0    0.964242
1    0.035758
Name: proportion, dtype: float64

In [580]:
# сбалансируем данные в y_train_pd
list_c1_percent_id = class_1_percent_samples(y_train_pd,0.5)
# list_c1_percent_features - список 'id' из y_train_pd соотвествующих  
# заданному проценту класса 1
len(list_c1_percent_id)

45860

In [581]:
# проверим сбалансированность полученного y_train
y_train_pd.loc[list_c1_percent_id]['flag'].value_counts(normalize=True)

flag
1    0.5
0    0.5
Name: proportion, dtype: float64

*transform_data_torow*, показываеются последние N операций клиента.  
В данных в *date_torow*, собраны последние 25 операций клиентов.

Предварительный анализ показывает, что медиальное значение количества клиентских  
операций равно 7. Поэтому, для начала, будем показывать моделе $n_{last} = 7$   
последних клиентских операций.

Для извлечения из *transform_data_torow_25* необходимого количества последних клиенских  
операций ($n_{last}$) используем функцию features_from_transform_data_torow.

Функция features_from_transform_data_torow примает следующие аргументы:
- $n_{last} = 7$ - необходимое количество последних клиентских операций; 
- $n_{groups} = 8$ - количество признаков в $date$ $features$;
- $N_{last} = 25$ - количество $n_{last}$ операций, показанных в transform_data_torow_25


In [582]:
# с помощью функции features_from_transform_data_torow извлечем  
# из данных transform_data_torow_25
# признаки сооствествующие 7 последним клиенским операциям
list_n_last_features = features_from_transform_data_torow(7,count_features,25)

In [583]:
# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']
# сформируем данные для проверики модели
X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

In [584]:
# посмотрим на структуру данных в X_train_balanced
X_train_balanced.head(2)

f1  f2  f3  f4  f5  f6  f7  f8  f9  f10  ...  f91  f92  f93  f94  \
id                                                ...                       
2335465   1   1   1   1   1   1   1   1   1    1  ...    1    1    0    0   
390270    1   1   1   1   1   1   0   0   0    0  ...    0    0    0    0   

         f95  f96  f97  f98  f99  f100  
id                                      
2335465    0    0    0    0    0     0  
390270     0    0    0    0    0     0  

[2 rows x 100 columns]

In [585]:
# посмотрим на структуру данных в y_train_balanced
y_train_balanced.head(2)

id
2335465    1
390270     1
Name: flag, dtype: int64

In [586]:
# проверим что выборки действительно совпадают по id
X_train_balanced.index.to_list() == y_train_balanced.index.to_list()

True

##### <span style="color:MediumSlateBlue">Baseline обучение модели Hist Gradient Boosting Classifier</span>

In [587]:
# обучаем модель Gradient Boosting Classifier
gradient_boosting = HistGradientBoostingClassifier(random_state=42)
gradient_boosting.fit(np.array(X_train_balanced)[:,list_n_last_features],np.array(y_train_balanced))

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_rf__pred_proba = gradient_boosting.predict_proba(X_train[:,list_n_last_features])[:,1]
y_valid_rf_pred_proba = gradient_boosting.predict_proba(X_valid[:,list_n_last_features])[:,1]

# Делаем предсказание для валидационной выборки
y_valid_rf_pred = gradient_boosting.predict(X_valid[:,list_n_last_features])

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_rf__pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_rf_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_rf_pred))

# time: 

ROC AUC на обучающем наборе 0.646
ROC AUC на валидационном наборе 0.633
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.98      0.62      0.76     68747
           1       0.05      0.57      0.09      2503

    accuracy                           0.61     71250
   macro avg       0.51      0.59      0.42     71250
weighted avg       0.94      0.61      0.73     71250



##### <span style="color:MediumSlateBlue">Подбор гиперпараметров модели</span>

In [1655]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'service'
count_features = dict_spaces[feature_space]

# настроим оптимизацию гипер параметров
def optuna_hgbc(trial):
  # задаем пространства поиска гиперпараметров
  learning_rate = trial.suggest_float('learning_rate',0.2,0.6)
  max_iter = trial.suggest_int('max_iter', 50, 300,step = 1)
  max_leaf_nodes = trial.suggest_int('max_leaf_nodes', 2, 50,step = 1)
  max_depth = trial.suggest_int('max_depth', 1, 15,step = 1)
  min_samples_leaf = trial.suggest_int('min_samples_leaf', 1, 50,step = 1)
  max_features = trial.suggest_float('max_features',0.1,1)
  l2_regularization = trial.suggest_float('l2_regularization',0.01,1)
  class_0_weight = trial.suggest_float('class_0_weight',0.01,1)
  class_1_weight = trial.suggest_float('class_1_weight',0.01,1)
  n_last = trial.suggest_int('n_last', 5, 25,step = 1)
  class_1_percent = trial.suggest_float('class_1_percent',0.01,1)
  random_state = trial.suggest_int('random_state', 1, 1000000)


  # создаем модель
  optuna_gradient_boosting = HistGradientBoostingClassifier(
      learning_rate= learning_rate,
      max_iter = max_iter,
      max_leaf_nodes =max_leaf_nodes,
      max_depth = max_depth,
      min_samples_leaf = min_samples_leaf,
      max_features=max_features,
      l2_regularization = l2_regularization,
      class_weight={0:class_0_weight,1:class_1_weight},
      random_state=42)

  # с помощью функции features_from_transform_data_torow извлечем  
  # из данных transform_data_torow
  # признаки сооствествующие n_last последним клиенским операциям
  list_n_last_features = features_from_transform_data_torow(n_last,count_features,25)

  # загружаем обучующие наборы
  X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
  y_train_pd = pd.read_csv('target/target_train.csv')

  # поготовим данные y_train_pd к работе с функцией class_1_percent_samples
  y_train_pd.set_index('id',drop=False,inplace=True)

  # подготовим данные для обучения модели
  # с помощью функции class_1_percent_samples зададим долю класса 1
  list_c1_percent_id = class_1_percent_samples(y_train_pd,class_1_percent,random_state=random_state)[:1000000]

  # сформируем данные для обучения модели
  X_train_balanced = np.array(X_train_pd.loc[list_c1_percent_id])[:,list_n_last_features]
  y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

  # освободим память от "тяжелых" и ненужных файлов
  del X_train_pd, y_train_pd
  gc.collect()

  # я не воспользовался параметром timeout метода optimize потому, что  
  # optimize отставливает поиск параметров, если время обучения 
  # превышает timeout. Мне нужно чтобы поиск параметров продолжился.
  try:
    # для модуля func_time_out упакуем обучение модели в функцию try_func
    def try_func():
            return optuna_gradient_boosting.fit(X_train_balanced,y_train_balanced)
    # обучаем модель с ограничением по времени 10 минут (600 секунд)
    optuna_gradient_boosting = func_timeout.func_timeout(600, try_func)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train_balanced, y_train_balanced
    gc.collect()

    # подгружаем данные для тестирования
    X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()[:,list_n_last_features]
    y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
    X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()[:,list_n_last_features]
    y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

    # делаем предсказание на обучающем и валидационном наборе и считаем метрики
    roc_train = metrics.roc_auc_score(y_train, optuna_gradient_boosting.predict_proba(X_train)[:,1])
    roc_valid = metrics.roc_auc_score(y_valid, optuna_gradient_boosting.predict_proba(X_valid)[:,1])
    f1_score = metrics.f1_score(y_valid, optuna_gradient_boosting.predict(X_valid))
    recall_1 = metrics.recall_score(y_valid, optuna_gradient_boosting.predict(X_valid),average=None,zero_division=0)[1]
    precision_1 = metrics.precision_score(y_valid, optuna_gradient_boosting.predict(X_valid),average=None,zero_division=0)[1]

    # удаляем крупные файлы чтобы высвободить память 
    del X_train, X_valid, y_train, y_valid 
    gc.collect()

  except func_timeout.FunctionTimedOut:
    # освободим память от "тяжелых" и ненужных файлов
    del X_train_balanced, y_train_balanced
    gc.collect()

    # обьявим метрики пустыми значениями
    roc_train = 0
    roc_valid = 0
    f1_score = 0
    recall_1 = 0
    precision_1 = 0
    pass

  return roc_train, roc_valid, f1_score, recall_1, precision_1

In [1656]:
# cоздаем объект исследования
# чтобы модель не переобучалась минимизируем roc_train 
# и максимизируем roc_valid
optuna_study_hsbs = optuna.create_study(study_name='HistGradientBoostingClassifier_'+feature_space+'_torow', 
                               directions=['maximize','maximize','maximize','maximize','maximize'], 
                               sampler=optuna.samplers.TPESampler(),
                               pruner='Hyperband',
                               storage='sqlite:///optuna_studies.db',
                               load_if_exists=True)

# ну случай удаления обучения
# optuna.delete_study(study_name='HistGradientBoostingClassifier_'+feature_space+'_torow', storage='sqlite:///optuna_studies.db')

[I 2025-04-19 14:31:56,395] Using an existing study with name 'HistGradientBoostingClassifier_service_torow' instead of creating a new one.


In [590]:
# ищем лучшую комбинацию гиперпараметров n_trials раз
optuna_study_hsbs.optimize(optuna_hgbc, n_trials=300)

[I 2025-04-17 19:15:29,244] Trial 0 finished with values: [0.6172205779505678, 0.6175846173995834, 0.08970976253298153, 0.09508589692369157, 0.0849090260435248] and parameters: {'learning_rate': 0.24325867493374545, 'max_iter': 56, 'max_leaf_nodes': 45, 'max_depth': 1, 'min_samples_leaf': 48, 'max_features': 0.7589320659029519, 'l2_regularization': 0.734053778753134, 'class_0_weight': 0.0974846014701767, 'class_1_weight': 0.12444550155600753, 'n_last': 14, 'class_1_percent': 0.3366989143087686, 'random_state': 113125}.
[I 2025-04-17 19:15:32,815] Trial 1 finished with values: [0.6387337594696196, 0.6267110680182166, 0.06923357561810681, 0.9856172592888534, 0.035876852377005074] and parameters: {'learning_rate': 0.21971043933659176, 'max_iter': 281, 'max_leaf_nodes': 38, 'max_depth': 8, 'min_samples_leaf': 35, 'max_features': 0.5372642052290924, 'l2_regularization': 0.11658941048035752, 'class_0_weight': 0.7229845324340504, 'class_1_weight': 0.44458660552089363, 'n_last': 13, 'class_1_p

In [1657]:
# из полученного результат соврмируем Data Frame
optuna_study_hsbs_pd = optuna_study_hsbs.trials_dataframe()
# переименуем столбы
optuna_study_hsbs_pd.rename(columns={
    'values_0': 'roc_train',
    'values_1': 'roc_valid',
    'values_2': 'f1_score',
    'values_3': 'recall_1',
    'values_4': 'precision_1'
},inplace=True)
# Выделим время потраченное на обучение модели
last_trail = optuna_study_hsbs_pd['number'].max()
optuna_study_hsbs_pd.tail(5)


number  roc_train  roc_valid  f1_score  recall_1  precision_1  \
295     295   0.670899   0.636532  0.095426  0.106272     0.086589   
296     296   0.656207   0.633204  0.069222  0.990012     0.035865   
297     297   0.646931   0.636672  0.067917  0.999201     0.035153   
298     298   0.644888   0.634490  0.069238  0.991610     0.035871   
299     299   0.673225   0.636222  0.095333  0.095885     0.094787   

                datetime_start          datetime_complete  \
295 2025-04-17 19:45:29.931440 2025-04-17 19:45:40.267283   
296 2025-04-17 19:45:40.273028 2025-04-17 19:45:48.348980   
297 2025-04-17 19:45:48.355452 2025-04-17 19:45:56.181437   
298 2025-04-17 19:45:56.187284 2025-04-17 19:46:03.817971   
299 2025-04-17 19:46:03.823909 2025-04-17 19:46:14.632614   

                  duration  params_class_0_weight  ...  \
295 0 days 00:00:10.335843               0.080551  ...   
296 0 days 00:00:08.075952               0.063120  ...   
297 0 days 00:00:07.825985               0.031880  ...   
298 0 days 00:00:07.630687               0.337410  ...   
299 0 days 00:00:10.808705               0.088986  ...   

     params_l2_regularization  params_learning_rate  params_max_depth  \
295                  0.474546              0.462210                 7   
296                  0.522529              0.316142                 7   
297                  0.542226              0.317626                 8   
298                  0.180044              0.387744                 6   
299                  0.567968              0.329682                 8   

     params_max_features  params_max_iter  params_max_leaf_nodes  \
295             0.824418               99                     33   
296             0.935182              226                     27   
297             0.703196              222                     18   
298             0.918229              172                     17   
299             0.904659              233                     29   

     params_min_samples_leaf  params_n_last  params_random_state     state  
295                       29             19               356863  COMPLETE  
296                       29             20               327526  COMPLETE  
297                       34             19               143764  COMPLETE  
298                       33             20               755889  COMPLETE  
299                       28             22               160980  COMPLETE  

[5 rows x 22 columns]

In [1658]:
# покаждем статистику обучения
print('Максимальное значение метрики ROC AUC на валидационном наборе:',round(optuna_study_hsbs_pd['roc_valid'].max(),3))
print('Среднее значение метрики ROC AUC на валидационном наборе:',round(optuna_study_hsbs_pd['roc_valid'].mean(),3))
print('Максимальное значение метрики f1_score на валидационном наборе:',round(optuna_study_hsbs_pd['f1_score'].max(),3))
print('Среднее значение метрики f1_score на валидационном наборе:',round(optuna_study_hsbs_pd['f1_score'].mean(),3))
print('Максимальное значение метрики recall_1 на валидационном наборе:',round(optuna_study_hsbs_pd['recall_1'].max(),3))
print('Среднее значение метрики recall_1 на валидационном наборе:',round(optuna_study_hsbs_pd['recall_1'].mean(),3))
print('Максимальное значение метрики precision_1 на валидационном наборе:',round(optuna_study_hsbs_pd['precision_1'].max(),3))
print('Среднее значение метрики precision_1 на валидационном наборе:',round(optuna_study_hsbs_pd['precision_1'].mean(),3))

Максимальное значение метрики ROC AUC на валидационном наборе: 0.641
Среднее значение метрики ROC AUC на валидационном наборе: 0.634
Максимальное значение метрики f1_score на валидационном наборе: 0.114
Среднее значение метрики f1_score на валидационном наборе: 0.073
Максимальное значение метрики recall_1 на валидационном наборе: 1.0
Среднее значение метрики recall_1 на валидационном наборе: 0.42
Максимальное значение метрики precision_1 на валидационном наборе: 0.267
Среднее значение метрики precision_1 на валидационном наборе: 0.08


In [1660]:
# Построим зависимость метрик качества модели от number

fig = px.scatter(
    data_frame=optuna_study_hsbs_pd[(optuna_study_hsbs_pd['roc_valid']>0.9999*optuna_study_hsbs_pd['roc_valid'].max())
                                    ],
    x='number', #ось абсцисс
    y=['roc_train','roc_valid','recall_1','precision_1'], #ось ординат
)
fig.update_layout(
    title ={
        'text':'Зависимость precision от гиперпараметров модели', # Имя рабочей плоскости
        'font':{'size':35,'family':"Times New Roman"}, # размер и стиль написания имени рабочей плоскости
        'x':0.5, # Смешение имени по оси "x" на половину рабочей плоскости
        },
    height =800,# Высота рабочей плоскости
    width = 1350, # Ширина рабочей плоскости
    bargap=0.2, # Добавил расстояния между столбами гистограммы
    xaxis_title='Величина optuna number',
    yaxis_title='Величина метрики')
fig.update_xaxes(showspikes=True)
fig.update_yaxes(showspikes=True)

fig.show()

<span style="color:Blue">

Вывод:  

Их всех выбираем точку $number =99$.   
В этой точке оптимальные значения метрик $recall_1$ и $precision_1$, а  
также относительно высокая метрика $ROC AUC$.   
Посмотрим каким значениям гиперпараметров соотвествует выбранная точка.

In [1662]:
# определим номер лучшге варианта
best_optuna_number = 99

# сформируем словарь лучших гипирпарметров RandomForestClassifier
best_param_rf = {
    'learning_rate' : optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_learning_rate'].iloc[0],
    'max_iter' : optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_max_iter'].iloc[0],
    'max_leaf_nodes' : optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_max_leaf_nodes'].iloc[0],
    'max_depth' : optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_max_depth'].iloc[0],
    'min_samples_leaf' : optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_min_samples_leaf'].iloc[0],
    'max_features' : optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_max_features'].iloc[0],
    'l2_regularization' : optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_l2_regularization'].iloc[0],
    'class_weight' : {0: optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_class_0_weight'].iloc[0],
                      1: optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_class_1_weight'].iloc[0],}
    }

# определим перменные для лучших значений параметров
best_n_last = optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_n_last'].iloc[0]
best_class_1_percent = optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_class_1_percent'].iloc[0]
best_random_state = optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['params_random_state'].iloc[0]


# Выведем принятые наилучшие праметры
print('best learning rate:',round(best_param_rf['learning_rate'],3))
print('best max iter:',best_param_rf['max_iter'])
print('best max leaf nodes:',best_param_rf['max_leaf_nodes'])
print('best max depth:',best_param_rf['max_depth'])
print('best min samples leaf:',best_param_rf['min_samples_leaf'])
print('best max features:',round(best_param_rf['max_features'],3))
print('best l2 regularization:',round(best_param_rf['l2_regularization'],3))
print('best class 0 weight:',round(best_param_rf['class_weight'][0],3))
print('best class 1 weight:',round(best_param_rf['class_weight'][1],3))

print('best class 1 percent:',round(best_class_1_percent,3))
print('best n last:',best_n_last)
print('best random state:',best_random_state)
print('time for best train:',round(optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['duration'].iloc[0].seconds/60),'minutes')

print()
print('ROC AUC на обучающем наборе:', round(optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['roc_train'].iloc[0],3))
print('ROC AUC на валидационном наборе:', round(optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['roc_valid'].iloc[0],3))
print('precision класса 1:', round(optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['precision_1'].iloc[0],3))
print('recall класса 1:', round(optuna_study_hsbs_pd[optuna_study_hsbs_pd['number']==best_optuna_number]['recall_1'].iloc[0],3))

best learning rate: 0.236
best max iter: 209
best max leaf nodes: 17
best max depth: 9
best min samples leaf: 17
best max features: 0.529
best l2 regularization: 0.437
best class 0 weight: 0.112
best class 1 weight: 0.973
best class 1 percent: 0.206
best n last: 17
best random state: 566239
time for best train: 0 minutes

ROC AUC на обучающем наборе: 0.655
ROC AUC на валидационном наборе: 0.641
precision класса 1: 0.037
recall класса 1: 0.968


##### <span style="color:MediumSlateBlue">Обучение модели с лучшими параметрами</span>

In [1663]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'service'
count_features = dict_spaces[feature_space]

# с помощью функции features_from_transform_data_torow извлечем  
# из данных transform_data_torow
# признаки сооствествующие n_last последним клиенским операциям
list_n_last_features = features_from_transform_data_torow(best_n_last,count_features,25)

# загружаем обучующие наборы
X_train_pd = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)

# подготовим данные для обучения модели
# с помощью функции class_1_percent_samples зададим долю класса 1
list_c1_percent_id = class_1_percent_samples(y_train_pd,best_class_1_percent,random_state=best_random_state)[:1000000]

# сформируем данные для обучения модели
X_train_balanced = np.array(X_train_pd.loc[list_c1_percent_id])[:,list_n_last_features]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

# освободим память от "тяжелых" и ненужных файлов
del X_train_pd, y_train_pd
gc.collect()


# обучаем модель HistGradientBoostingClassifier с наилучшеми параметрами
gradient_boosting = HistGradientBoostingClassifier(
        **best_param_rf,
        random_state=42)
gradient_boosting.fit(X_train_balanced,y_train_balanced)

# освободим память от "тяжелых" и ненужных файлов
del X_train_balanced, y_train_balanced
gc.collect()

# подгружаем данные для тестирования
X_train = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_train').to_pandas().to_numpy()[:,list_n_last_features]
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
X_valid = fp.ParquetFile('features/base_models/torow/'+feature_space+'_torow_valid').to_pandas().to_numpy()[:,list_n_last_features]
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_gb__pred_proba = gradient_boosting.predict_proba(X_train)[:,1]
y_valid_gb_pred_proba = gradient_boosting.predict_proba(X_valid)[:,1]

# Делаем предсказание для валидационной выборки
y_valid_gb_pred = gradient_boosting.predict(X_valid)

# освободим память от "тяжелых" и ненужных файлов
del X_train, X_valid
gc.collect()

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_gb__pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_gb_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_gb_pred,zero_division=0))

# time: 2m 30s

ROC AUC на обучающем наборе 0.655
ROC AUC на валидационном наборе 0.641
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.99      0.09      0.17     68747
           1       0.04      0.97      0.07      2503

    accuracy                           0.12     71250
   macro avg       0.51      0.53      0.12     71250
weighted avg       0.95      0.12      0.17     71250



### <span style="color:RoyalBlue">Построение модели на сбалансированных данных подпрострнства date stat</span>

#### <span style="color:MediumBlue">Построение модели Logistic Regression</span>

##### <span style="color:MediumSlateBlue">Формирование данных для обучения</span>

Анализ исходных данных, в частности target, показал что представленные данные   
имееют перекос: 96% клиентов у которых не случился дефолт (flag = 0),    
против 4 % - для которых произошел дефолт (flag = 1).  
С помощью функции class_1_percent_samples, сформируем сбаланисрованную выборку  
для обучения моделей.
За основу сбалансировных данных возьмем данные клиентов с дефолтом  
и к ним будем добирать необходимое количество клиентов до сбалансированности. 


Функция class_1_percent_samples принемает две переменные:
- target_data - массив с id и целевой переменной
- class_1_percent - процент класса 1 в результирующем массиве

In [610]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'date'
count_features = dict_spaces[feature_space]

In [611]:
# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

In [612]:
# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)
y_train_pd.head(4)

id  flag
id                    
1825800  1825800     0
2166483  2166483     0
2534345  2534345     0
1803283  1803283     0

In [613]:
# взглянем на сблансиорованность данных в y_train
y_train_pd['flag'].value_counts(normalize=True)

flag
0    0.964242
1    0.035758
Name: proportion, dtype: float64

In [614]:
# сбалансируем данные в y_train_pd
list_c1_percent_id = class_1_percent_samples(y_train_pd,0.5)
# list_c1_percent_features - список 'id' из y_train_pd соотвествующих  
# заданному проценту класса 1
len(list_c1_percent_id)

45860

In [615]:
# проверим сбалансированность полученного y_train
y_train_pd.loc[list_c1_percent_id]['flag'].value_counts(normalize=True)

flag
1    0.5
0    0.5
Name: proportion, dtype: float64

В отличие от данных в *transform_data_torow*, где модели показываеются последние N  
операций клиента, в данные в *transform_data_stat* сфомированы из различных статистических   
характеристик ряда определяющего клиентскую историю в банке. 

Соотвественно, если в данных *transform_data_torow* была сильная корреляция между признаками,  
то я не смог бы ее убрать, иначе потярется смысл "показать последовательный ряд в историии клиента".  
Признаки в *transform_data_stat* не имеют такой особенности. Поэтому, необходимо проанализировать  
данные в *transform_data_stat* и, в случае сильной коррреляции признаков, устранить ее.

In [616]:
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()
corr_matrix.shape

(137, 137)

In [617]:
# с помощью функции corr_transrom_to_power получим
# силу корреляции матрицы и список не коррелируемых признаков

# для начального анализа зададим порог силы корреляции, при котором признаки 
# будут отнесены к "сильно скоррелированными" равным 0.6
ncorr_matrix,list_ncorr_features,corr_power =corr_transform_to_force(corr_matrix,threshold=0.6)

# Выведем результаты преобразования
print('Исходное количество признаков: ', corr_matrix.shape[0])
print('Количество не коррелируемых признаков: ', len(list_ncorr_features))
# сила корреляции признаков
print('Отношение коррелируемых исходному количеству признаков (сила корреляции): ',corr_power)

Исходное количество признаков:  137
Количество не коррелируемых признаков:  42
Отношение коррелируемых исходному количеству признаков (сила корреляции):  0.693


In [618]:
# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']
# сформируем данные для проверики модели
# сформируем данные для анализа сбалансированности обучающих данных
X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()
y_train = pd.read_csv('target/target_train.csv')['flag']
X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()
y_valid = pd.read_csv('target/target_valid.csv')['flag']

In [619]:
# посмотрим на структуру данных в X_train_balanced
X_train_balanced.head(4)

f1    f2      f3      f4      f5      f6      f7   f8     f9  f10  \
id                                                                             
2335465  17.0  16.0   9.059   7.140   7.140  17.387   9.059  0.0  5.641  2.0   
390270    6.0  12.0  15.000  14.260  14.260  18.587  15.000  0.0  4.123  7.0   
2494034  14.0  15.0   9.714   8.242   8.242  16.484   9.714  0.0  4.832  2.0   
2018674  15.0  16.0   9.200   0.000   0.000  15.375   9.200  0.0  6.134  0.0   

         ...   f128  f129  f130  f131  f132  f133  f134  f135   f136  f137  
id       ...                                                                
2335465  ...  0.381   0.0   0.0   0.0   0.0   1.0   0.0  0.82  0.154   0.5  
390270   ...  0.500   0.0   0.0   0.5   1.0   1.0   0.0  1.00  0.300   0.5  
2494034  ...  0.258   0.0   0.0   0.0   0.0   1.0   0.0  0.93  0.071   0.5  
2018674  ...  0.249   0.0   0.0   0.0   0.0   1.0   0.0  0.93  0.067   0.5  

[4 rows x 137 columns]

In [620]:
# посмотрим на структуру данных в y_train_balanced
y_train_balanced.head(4)

id
2335465    1
390270     1
2494034    1
2018674    1
Name: flag, dtype: int64

In [621]:
# проверим что выборки действительно совпадают по id
X_train_balanced.index.to_list() == y_train_balanced.index.to_list()

True

##### <span style="color:MediumSlateBlue">Baseline обучение модели LogisticRegression</span>

In [622]:
# обучаем модель логистической регрессии
logistic_regression = linear_model.LogisticRegression(random_state=42, max_iter=10000)
logistic_regression.fit(X_train_balanced[list_ncorr_features],y_train_balanced)

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_LR_pred_proba = logistic_regression.predict_proba(X_train[list_ncorr_features])[:,1]
y_valid_LR_pred_proba = logistic_regression.predict_proba(X_valid[list_ncorr_features])[:,1]

# Делаем предсказание для валидационной выборки
y_valid_LR_pred = logistic_regression.predict(X_valid[list_ncorr_features])

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_LR_pred_proba),3))
print('ROC AUC на тестовом наборе', round(metrics.roc_auc_score(y_valid, y_valid_LR_pred_proba),3))

print('Основные метрики на тестовом наборе:')
print(metrics.classification_report(y_valid,y_valid_LR_pred))

# time: 3m 5s

ROC AUC на обучающем наборе 0.571
ROC AUC на тестовом наборе 0.566
Основные метрики на тестовом наборе:
              precision    recall  f1-score   support

           0       0.97      0.62      0.75     68747
           1       0.04      0.47      0.08      2503

    accuracy                           0.61     71250
   macro avg       0.51      0.54      0.42     71250
weighted avg       0.94      0.61      0.73     71250



##### <span style="color:MediumSlateBlue">Анализ влияния scaler преобразования на качество и скорость схождения модели</span>

In [623]:
# формируем список из необходимых scaler
scalers = [MinMaxScaler(),RobustScaler() ,StandardScaler()]

# сформируем списко для заполнения данными результатов анализа
scalers_data = []

# установим ограничение на время обучения модели в 600 секунд (10 минут)
time_out = 600

for scaler in scalers:
        # для того чтобы следить за выполнением цикла введем индикатор
        print('current scaler: ', scaler)

         # сформируем список для заполнения данными текушего scaler
        current_scaler_data = [scaler]
        
        # выполним scaler преобразование
        X_train_s_balanced = scaler.fit_transform(X_train_balanced[list_ncorr_features])
        X_train_s = scaler.transform(X_train[list_ncorr_features])
        X_valid_s = scaler.transform(X_valid[list_ncorr_features])

        try:
                # для модуля func_time_out упакуем обучение модели в функцию try_func
                def try_func():
                        logistic_regression = linear_model.LogisticRegression(random_state=42, max_iter=10000)
                        return logistic_regression.fit(X_train_s_balanced,y_train_balanced)
                    
                # фиксируем время начала
                start_time = time.time()
                
                # запускаем обучение модели с ограничением по времени
                logistic_regression = func_timeout.func_timeout(time_out, try_func)
                
                # фиксируем время окончания обучения
                end_time = time.time()
                
                # запишем время обучения модели
                current_scaler_data.append(round(end_time-start_time))

                # Делаем предсказание для обучающей и валидационной выборки
                y_valid_lr_pred = logistic_regression.predict(X_valid_s)
                
                # для метрик ROC AUC делаем предсказание модели для обучающей и валидационной выборки  
                # в виде вероятности принадлежности к классу 1 
                y_train_lr_pred_proba = logistic_regression.predict_proba(X_train_s)[:,1]
                y_valid_lr_pred_proba = logistic_regression.predict_proba(X_valid_s)[:,1]

                #Считаем метрики ROC AUC yна обуающем и валидационном наборе и добавляем их в спискок
                current_scaler_data.append(round(metrics.roc_auc_score(y_train, y_train_lr_pred_proba),3))
                current_scaler_data.append(round(metrics.roc_auc_score(y_valid, y_valid_lr_pred_proba),3))

                #Считаем метрики для класса 0 на валидационном наборе и добавляем их в список
                current_scaler_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))
                current_scaler_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))


                #Считаем метрики для класса 1 на валидационном набопе и добавляем их в список
                current_scaler_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))
                current_scaler_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))

                # добавляем полученные данные в список scalers_data
                scalers_data.append(current_scaler_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                scaler_pd =pd.DataFrame(
                        columns=['scaler','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = scalers_data)
                # сохраняем dataframe
                scaler_pd.to_csv('data_recovery/scaler_pd.csv',index=False)
               
                # очистим output от прошедшей итерации
                clear_output()

        except func_timeout.FunctionTimedOut:
                # если время обучения привышает лимит
                # запишем в current_scaler_data соотвествующую данные
                current_scaler_data = [scaler,'>30m',0,0,0,0,0,0]
                # добавляем полученные данные в список scalers_data
                scalers_data.append(current_scaler_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                scaler_pd =pd.DataFrame(
                        columns=['scaler','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = scalers_data)
                # сохраняем dataframe
                scaler_pd.to_csv('data_recovery/scaler_pd.csv',index=False)
                
                # очистим output от прошедшей итерации
                clear_output()
                # переходим к следующему scaler
                pass
# очистим output
clear_output()

# сформируем данные соотвествующие лучщему ROC AUC на валидацинном наборе
best_roc_valid_data = scaler_pd[scaler_pd['roc_valid']==scaler_pd['roc_valid'].max()]

# выведем лучший результат на валидационном наборе
print('result:')
print('best scaler on valid:',best_roc_valid_data.iloc[0]['scaler'])
print('ROC AUC on train:', best_roc_valid_data.iloc[0]['roc_train'])
print('ROC AUC on valid:', best_roc_valid_data.iloc[0]['roc_valid'])
print('Time fit for best scaler:', best_roc_valid_data.iloc[0]['time_fit'],' seconds')

# выведем полученный dataframe
scaler_pd

# time: 

result:
best scaler on valid: MinMaxScaler()
ROC AUC on train: 0.571
ROC AUC on valid: 0.566
Time fit for best scaler: 0  seconds


scaler  time_fit  roc_train  roc_valid  recall_0  precision_0  \
0    MinMaxScaler()         0      0.571      0.566     0.618         0.97   
1    RobustScaler()         0      0.571      0.566     0.616         0.97   
2  StandardScaler()         0      0.571      0.566     0.616         0.97   

   recall_1  precision_1  
0     0.467        0.043  
1     0.469        0.043  
2     0.470        0.043

##### <span style="color:MediumSlateBlue"> Анализ влияния solver оптимизатора на качество и скорость обучения модели</span>

Проверим качество и скорость сходимости модели при разных solver  
Проверку осуществим через цикл  
Чтобы модель не сходилась бесконечно с помощью модуля func_timeout  
поставим ограничение времени схождения в 10 минут

In [624]:
# подготовим данные для обучения модели

# обьявим scaler
scaler = StandardScaler()
# выполним scaler преобразование
X_train_s_balanced = scaler.fit_transform(X_train_balanced[list_ncorr_features])
X_train_s = scaler.transform(X_train[list_ncorr_features])
X_valid_s = scaler.transform(X_valid[list_ncorr_features])

# time: 10s

In [625]:
# Зададим список solvers
solvers_list = ['lbfgs', 'liblinear', 'newton-cg', 'newton-cholesky', 'sag', 'saga']

# сформируем список для заполнения
solvers_data = []

# установим ограничение на время обучения модели в 180 секунд (3 минут)
time_out = 180

for solver in solvers_list:
        # для того чтобы следить за выполнением цикла введем индикатор
        print('current solver: ', solver)

         # сформируем список для заполнения данными текушего solver
        current_solver_data = [solver]
        
        try:
                # для модуля func_time_out упакуем обучение модели в функцию try_func
                def try_func():
                        logistic_regression = linear_model.LogisticRegression(solver= solver,
                                                                  random_state=42, 
                                                                  max_iter=10000)
                        return logistic_regression.fit(X_train_s_balanced,y_train_balanced)
                    
                # фиксируем время начала
                start_time = time.time()
                
                # запускаем обучение модели с ограничением по времени
                logistic_regression = func_timeout.func_timeout(time_out, try_func)
                
                # фиксируем время окончания обучения
                end_time = time.time()
                
                # запишем время обучения модели
                current_solver_data.append(round(end_time-start_time))

                # Делаем предсказание для обучающей и валидационной выборки
                y_valid_lr_pred = logistic_regression.predict(X_valid_s)
                
                # для метрик ROC AUC делаем предсказание модели для обучающей и валидационной выборки  
                # в виде вероятности принадлежности к классу 1 
                y_train_lr_pred_proba = logistic_regression.predict_proba(X_train_s)[:,1]
                y_valid_lr_pred_proba = logistic_regression.predict_proba(X_valid_s)[:,1]

                #Считаем метрики ROC AUC yна обуающем и валидационном наборе и добавляем их в спискок
                current_solver_data.append(round(metrics.roc_auc_score(y_train, y_train_lr_pred_proba),3))
                current_solver_data.append(round(metrics.roc_auc_score(y_valid, y_valid_lr_pred_proba),3))

                #Считаем метрики для класса 0 на валидационном наборе и добавляем их в список
                current_solver_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))
                current_solver_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))


                #Считаем метрики для класса 1 на валидационном набопе и добавляем их в список
                current_solver_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))
                current_solver_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))

                # запишем данные полученные на одной итерации
                solvers_data.append(current_solver_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                solvers_pd =pd.DataFrame(
                        columns=['solver','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = solvers_data)
                # сохраняем dataframe
                solvers_pd.to_csv('data_recovery/solvers_pd.csv',index=False)
               
                # очистим output от прошедшей итерации
                clear_output()

        except func_timeout.FunctionTimedOut:
                # если время обучения привышает лимит
                # запишем в current_solver_data соотвествующую данные
                current_solver_data = [solver,'>3m',0,0,0,0,0,0]
                # добавляем полученные данные в список solvers_data
                solvers_data.append(current_solver_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                solvers_pd =pd.DataFrame(
                        columns=['solver','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = solvers_data)
                # сохраняем dataframe
                solvers_pd.to_csv('data_recovery/solvers_pd.csv',index=False)
                
                # очистим output от прошедшей итерации
                clear_output()
                # переходим к следующему solver
                pass
# очистим output
clear_output()

# сформируем данные соотвествующие лучщему ROC AUC на валидацинном наборе
best_roc_valid_data = solvers_pd[solvers_pd['roc_valid']==solvers_pd['roc_valid'].max()]

# выведем лучший результат на валидационном наборе
print('result:')
print('best solver on valid:',best_roc_valid_data.iloc[0]['solver'])
print('ROC AUC on train:', best_roc_valid_data.iloc[0]['roc_train'])
print('ROC AUC on valid:', best_roc_valid_data.iloc[0]['roc_valid'])
print('Time fit for best solver:', best_roc_valid_data.iloc[0]['time_fit'],' seconds')

# выведем полученный dataframe
solvers_pd

# time: 2m 35s

result:
best solver on valid: lbfgs
ROC AUC on train: 0.571
ROC AUC on valid: 0.566
Time fit for best solver: 0  seconds


solver  time_fit  roc_train  roc_valid  recall_0  precision_0  \
0            lbfgs         0      0.571      0.566     0.616         0.97   
1        liblinear         0      0.571      0.566     0.616         0.97   
2        newton-cg         0      0.571      0.566     0.616         0.97   
3  newton-cholesky         0      0.571      0.566     0.616         0.97   
4              sag         0      0.571      0.566     0.616         0.97   
5             saga         0      0.571      0.566     0.616         0.97   

   recall_1  precision_1  
0     0.470        0.043  
1     0.469        0.043  
2     0.469        0.043  
3     0.469        0.043  
4     0.469        0.043  
5     0.469        0.043

##### <span style="color:MediumSlateBlue">Подбор гиперпараметров модели</span>

In [1664]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'date'
count_features = dict_spaces[feature_space]

# для работы функции corr_transform_to_force
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()

# для выбора sceler преобразвания нам понадобится словарь
dict_scalers ={
    'MinMaxScaler': MinMaxScaler(),
    'RobustScaler':RobustScaler(),
    'StandardScaler':StandardScaler()}

# настроим оптимизацию гипер параметров
def optuna_lg(trial):
  # задаем пространства поиска гиперпараметров
  solver = trial.suggest_categorical("solver", ['lbfgs', 'liblinear', 'newton-cg', 'newton-cholesky'])
  C = trial.suggest_float('C',0.01,1)
  class_0_weight = trial.suggest_float('class_0_weight',0.2,0.6)
  class_1_weight = trial.suggest_float('class_1_weight',0.2,0.6)
  threshold = trial.suggest_float('threshold',0.6,1)
  class_1_percent = trial.suggest_float('class_1_percent',0.01,0.3)
  scaler = trial.suggest_categorical("scaler", ['MinMaxScaler','RobustScaler','StandardScaler'])
  random_state = trial.suggest_int('random_state', 1, 1000000)


  # создаем модель
  optuna_log_reg = linear_model.LogisticRegression(
      solver=solver,
      C=C,
      class_weight={0:class_0_weight,1:class_1_weight},
      random_state=random_state,
      max_iter=10000)

  # с помощью функции corr_transform_to_force получим
  # список не коррелируемых признаков
  list_ncorr_features = corr_transform_to_force(corr_matrix,threshold=threshold)[1]

  # обьявим scaler
  scaler = dict_scalers[scaler]

  # сформируем данные для анализа сбалансированности обучающих данных
  X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
  y_train_pd = pd.read_csv('target/target_train.csv')

  # поготовим данные y_train_pd к работе с функцией class_1_percent_samples
  y_train_pd.set_index('id',drop=False,inplace=True)

  # подготовим данные для обучения модели
  # с помощью функции class_1_percent_samples зададим долю 
  # класса 1
  list_c1_percent_id = class_1_percent_samples(y_train_pd,class_1_percent,random_state=random_state)[:1000000]

  # подготовим данные для обучения
  X_train_s_balanced = scaler.fit_transform(X_train_pd.loc[list_c1_percent_id])
  y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

  # освободим память от "тяжелых" и ненужных файлов
  del X_train_pd, y_train_pd
  gc.collect()

  # я не воспользовался параметром timeout метода optimize потому, что  
  # optimize отставливает поиск параметров, если время обучения 
  # превышает timeout. Мне нужно чтобы поиск параметров продолжился.
  try:
    # для модуля func_time_out упакуем обучение модели в функцию try_func
    def try_func():
            return optuna_log_reg.fit(X_train_s_balanced, y_train_balanced)
    # обучаем модель с ограничением по времени 10 минут (600 секунд)
    optuna_log_reg = func_timeout.func_timeout(600, try_func)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train_s_balanced, y_train_balanced
    gc.collect()

    # загружаем тестовые наборы
    # сформируем данные для анализа сбалансированности обучающих данных
    X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
    X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()[list_ncorr_features]
    y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
    y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

    # подготовим данные для проверки модели
    X_train_s = scaler.transform(X_train)
    X_valid_s = scaler.transform(X_valid)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train, X_valid
    gc.collect()

    # делаем предсказание на обучающем и валидационном наборе и считаем метрики
    roc_train = metrics.roc_auc_score(y_train, optuna_log_reg.predict_proba(X_train_s)[:,1])
    roc_valid = metrics.roc_auc_score(y_valid, optuna_log_reg.predict_proba(X_valid_s)[:,1])
    f1_score = metrics.f1_score(y_valid, optuna_log_reg.predict(X_valid_s))
    recall_1 = metrics.recall_score(y_valid, optuna_log_reg.predict(X_valid_s),average=None,zero_division=0)[1]
    precision_1 = metrics.precision_score(y_valid, optuna_log_reg.predict(X_valid_s),average=None,zero_division=0)[1]

    # удаляем крупные файлы чтобы высвободить память 
    del X_train_s, X_valid_s, y_train, y_valid
    gc.collect()

  except func_timeout.FunctionTimedOut:
    # удаляем крупные файлы чтобы высвободить память 
    del X_train_s_balanced, y_train_balanced
    gc.collect()
    
    # фиксируем пустые значения метрик
    roc_train = 0
    roc_valid = 0
    f1_score = 0
    recall_1 = 0
    precision_1 = 0
    pass

  return roc_train, roc_valid, f1_score, recall_1, precision_1

In [1665]:
# cоздаем объект исследования
# чтобы модель не переобучалась минимизируем roc_train 
# и максимизируем roc_valid
optuna_study_lg = optuna.create_study(study_name='LogisticRegression_'+feature_space+'_stat', 
                               directions=['maximize','maximize','maximize','maximize','maximize'], 
                               sampler=optuna.samplers.TPESampler(),
                               pruner='Hyperband',
                               storage='sqlite:///optuna_studies.db',
                               load_if_exists=True)
# optuna.delete_study(study_name='LogisticRegression_'+feature_space+'_stat', storage='sqlite:///optuna_studies.db')

[I 2025-04-19 14:35:13,021] Using an existing study with name 'LogisticRegression_date_stat' instead of creating a new one.


In [628]:
# ищем лучшую комбинацию гиперпараметров n_trials раз
optuna_study_lg.optimize(optuna_lg, n_trials=300)

[I 2025-04-17 19:46:51,545] Trial 0 finished with values: [0.5707508119083788, 0.5666986922775161, 0.0, 0.0, 0.0] and parameters: {'solver': 'newton-cholesky', 'C': 0.04880134489049474, 'class_0_weight': 0.4050592650224629, 'class_1_weight': 0.3666095149422748, 'threshold': 0.7321614848924581, 'class_1_percent': 0.07349956279697957, 'scaler': 'MinMaxScaler', 'random_state': 207380}.
[I 2025-04-17 19:46:56,115] Trial 1 finished with values: [0.5869500491025667, 0.5816118683675273, 0.08570619067856637, 0.2417099480623252, 0.05208781747739991] and parameters: {'solver': 'newton-cholesky', 'C': 0.6951901911889697, 'class_0_weight': 0.20707667825904147, 'class_1_weight': 0.5995372339066082, 'threshold': 0.9952542041642645, 'class_1_percent': 0.2123906404903617, 'scaler': 'MinMaxScaler', 'random_state': 144283}.
[I 2025-04-17 19:47:00,356] Trial 2 finished with values: [0.5712090968877191, 0.5690706579105524, 0.0, 0.0, 0.0] and parameters: {'solver': 'newton-cg', 'C': 0.26469435096544747, 'c

In [1666]:
# из полученного результат соврмируем Data Frame
optuna_study_lg_pd = optuna_study_lg.trials_dataframe().dropna()
# переименуем столбы
optuna_study_lg_pd.rename(columns={
    'values_0': 'roc_train',
    'values_1': 'roc_valid',
    'values_2': 'f1_score',
    'values_3': 'recall_1',
    'values_4': 'precision_1'
},inplace=True)
# Выделим время потраченное на обучение модели
optuna_study_lg_pd.tail()

number  roc_train  roc_valid  f1_score  recall_1  precision_1  \
295     295   0.585775   0.580534  0.082146  0.108270     0.066178   
296     296   0.587369   0.581964  0.066762  0.065122     0.068487   
297     297   0.586286   0.581927  0.088926  0.214143     0.056114   
298     298   0.584371   0.579430  0.079248  0.630044     0.042283   
299     299   0.587178   0.581369  0.079602  0.626848     0.042500   

                datetime_start          datetime_complete  \
295 2025-04-17 20:16:46.699991 2025-04-17 20:16:53.308966   
296 2025-04-17 20:16:53.314241 2025-04-17 20:17:00.046647   
297 2025-04-17 20:17:00.052184 2025-04-17 20:17:06.282953   
298 2025-04-17 20:17:06.288167 2025-04-17 20:17:12.641451   
299 2025-04-17 20:17:12.647309 2025-04-17 20:17:20.597804   

                  duration  params_C  params_class_0_weight  \
295 0 days 00:00:06.608975  0.341411               0.331034   
296 0 days 00:00:06.732406  0.671149               0.342700   
297 0 days 00:00:06.230769  0.364945               0.318737   
298 0 days 00:00:06.353284  0.300710               0.200473   
299 0 days 00:00:07.950495  0.976523               0.202439   

     params_class_1_percent  params_class_1_weight  params_random_state  \
295                0.288329               0.528766               505237   
296                0.279156               0.512679               293477   
297                0.299652               0.565225               270744   
298                0.284538               0.541618               328799   
299                0.284822               0.544058               326928   

    params_scaler    params_solver  params_threshold     state  
295  MinMaxScaler        newton-cg          0.979785  COMPLETE  
296  MinMaxScaler        newton-cg          0.999940  COMPLETE  
297  MinMaxScaler  newton-cholesky          0.991762  COMPLETE  
298  MinMaxScaler        newton-cg          0.893892  COMPLETE  
299  MinMaxScaler        liblinear          0.985854  COMPLETE

In [1667]:
# покаждем статистику обучения
print('Максимальное значение метрики ROC AUC на валидационном наборе:',round(optuna_study_lg_pd['roc_valid'].max(),3))
print('Среднее значение метрики ROC AUC на валидационном наборе:',round(optuna_study_lg_pd['roc_valid'].mean(),3))
print('Максимальное значение метрики f1_score на валидационном наборе:',round(optuna_study_lg_pd['f1_score'].max(),3))
print('Среднее значение метрики f1_score на валидационном наборе:',round(optuna_study_lg_pd['f1_score'].mean(),3))
print('Максимальное значение метрики recall_1 на валидационном наборе:',round(optuna_study_lg_pd['recall_1'].max(),3))
print('Среднее значение метрики recall_1 на валидационном наборе:',round(optuna_study_lg_pd['recall_1'].mean(),3))
print('Максимальное значение метрики precision_1 на валидационном наборе:',round(optuna_study_lg_pd['precision_1'].max(),3))
print('Среднее значение метрики precision_1 на валидационном наборе:',round(optuna_study_lg_pd['precision_1'].mean(),3))

Максимальное значение метрики ROC AUC на валидационном наборе: 0.585
Среднее значение метрики ROC AUC на валидационном наборе: 0.58
Максимальное значение метрики f1_score на валидационном наборе: 0.091
Среднее значение метрики f1_score на валидационном наборе: 0.059
Максимальное значение метрики recall_1 на валидационном наборе: 0.651
Среднее значение метрики recall_1 на валидационном наборе: 0.186
Максимальное значение метрики precision_1 на валидационном наборе: 0.176
Среднее значение метрики precision_1 на валидационном наборе: 0.052


In [1669]:
# Визуализируем метрики полученные при optuna оптимизации
fig = px.scatter(
    data_frame=optuna_study_lg_pd[(optuna_study_lg_pd['roc_valid']>0.999*optuna_study_lg_pd['roc_valid'].max())],
    x='number', #ось абсцисс
    y=['roc_train','roc_valid','recall_1','precision_1'], #ось ординат
)
fig.update_layout(
    title ={
        'text':'Зависимость качества модели от trials optuna', # Имя рабочей плоскости
        'font':{'size':35,'family':"Times New Roman"}, # размер и стиль написания имени рабочей плоскости
        'x':0.5, # Смешение имени по оси "x" на половину рабочей плоскости
        },
    height =800,# Высота рабочей плоскости
    width = 1350, # Ширина рабочей плоскости
    bargap=0.2, # Добавил расстояния между столбами гистограммы
    xaxis_title='trials optuna',
    yaxis_title='Величина метрики')
fig.update_xaxes(showspikes=True)
fig.update_yaxes(showspikes=True)

fig.show()

<span style="color:Blue">

Вывод:  

Их всех выбираем точку $number =238$.   
В этой точке самые оптимальные значения $recall$ и $precision$.  
Посмотрим каким значениям гиперпараметров соотвествует выбранная точка.

In [1670]:
# определим номер лучшге варианта
best_optuna_number = 238

# сформируем словарь лучших гипирпарметров RandomForestClassifier
best_param_lr = {
    'solver' : optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_solver'].iloc[0],
    'C' : round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_C'].iloc[0],3),
    'class_weight' : {0:round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_class_0_weight'].iloc[0],3),
                      1:round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_class_1_weight'].iloc[0],3)},
    }

# создадим перменные
best_threshold = optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_threshold'].iloc[0]
best_scaler = optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_scaler'].iloc[0]
best_class_1_percent = optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_class_1_percent'].iloc[0]
best_random_state = optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_random_state'].iloc[0]

# Выведем принятые наилучшие праметры
print('best solver:',best_param_lr['solver'])
print('best C:',best_param_lr['C'])
print('best class 0 weight:',best_param_lr['class_weight'][0])
print('best class 1 weight:',best_param_lr['class_weight'][1])

print('best class 1 percent:',round(best_class_1_percent,3))
print('best scaler:',best_scaler)
print('best threshold:',round(best_threshold,3))
print('best best random state:',best_random_state)
print('time for best train:',round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['duration'].iloc[0].seconds/60),'minutes')

print()
print('ROC AUC на обучающем наборе:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['roc_train'].iloc[0],3))
print('ROC AUC на валидационном наборе:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['roc_valid'].iloc[0],3))
print('precision класса 1:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['precision_1'].iloc[0],3))
print('recall класса 1:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['recall_1'].iloc[0],3))


best solver: newton-cg
best C: 0.96
best class 0 weight: 0.209
best class 1 weight: 0.496
best class 1 percent: 0.276
best scaler: RobustScaler
best threshold: 1.0
best best random state: 317122
time for best train: 0 minutes

ROC AUC на обучающем наборе: 0.591
ROC AUC на валидационном наборе: 0.585
precision класса 1: 0.048
recall класса 1: 0.421


##### <span style="color:MediumSlateBlue">Обучение модели с лучшими параметрами</span>

In [1671]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'date'
count_features = dict_spaces[feature_space]

# для работы функции corr_transform_to_force
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()

# подготовим данные
# для выбора sceler преобразвания нам понадобится словарь
dict_scalers ={
    'MinMaxScaler': MinMaxScaler(),
    'RobustScaler':RobustScaler(),
    'StandardScaler':StandardScaler(),
}

# с помощью функции corr_transform_to_force получим
# список не коррелируемых признаков
list_ncorr_features = corr_transform_to_force(corr_matrix,threshold=best_threshold)[1]

# обьявим scaler
scaler = dict_scalers[best_scaler]

# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
y_train_pd = pd.read_csv('target/target_train.csv')

# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)

# подготовим данные для обучения модели
# с помощью функции class_1_percent_samples зададим долю 
# класса 1
list_c1_percent_id = class_1_percent_samples(y_train_pd,best_class_1_percent,random_state=best_random_state)[:1000000]

# подготовим данные для обучения
X_train_s_balanced = scaler.fit_transform(X_train_pd.loc[list_c1_percent_id])
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

# освободим память от "тяжелых" и ненужных файлов
del X_train_pd, y_train_pd
gc.collect()


# обучаем модель LogisticRegression с наилучшеми параметрами
logistic_regression = linear_model.LogisticRegression(
        **best_param_lr,
        random_state=42,
        max_iter=10000)
logistic_regression.fit(X_train_s_balanced, y_train_balanced)

# удаляем крупные файлы чтобы высвободить память 
del X_train_s_balanced, y_train_balanced
gc.collect()

# загружаем тестовые наборы
# сформируем данные для анализа сбалансированности обучающих данных
X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()[list_ncorr_features]
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

# подготовим данные для проверки модели
X_train_s = scaler.transform(X_train)
X_valid_s = scaler.transform(X_valid)

# удаляем крупные файлы чтобы высвободить память 
del X_train, X_valid
gc.collect()

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_lr_pred_proba = logistic_regression.predict_proba(X_train_s)[:,1]
y_valid_lr_pred_proba = logistic_regression.predict_proba(X_valid_s)[:,1]

# Делаем предсказание для валидационной выборки
y_valid_lr_pred = logistic_regression.predict(X_valid_s)

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_lr_pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_lr_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_lr_pred,zero_division=0))

# time: 2m 30s

ROC AUC на обучающем наборе 0.591
ROC AUC на валидационном наборе 0.585
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.97      0.70      0.81     68747
           1       0.05      0.42      0.09      2503

    accuracy                           0.69     71250
   macro avg       0.51      0.56      0.45     71250
weighted avg       0.94      0.69      0.79     71250



#### <span style="color:MediumBlue">Построение модели Random Forest Classifier</span>

##### <span style="color:MediumSlateBlue">Формирование данных для обучения</span>

Анализ исходных данных, в частности target, показал что представленные данные   
имееют перекос: 96% клиентов у которых не случился дефолт (flag = 0),    
против 4 % - для которых произошел дефолт (flag = 1).  
С помощью функции class_1_percent_samples, сформируем сбаланисрованную выборку  
для обучения моделей.
За основу сбалансировных данных возьмем данные клиентов с дефолтом  
и к ним будем добирать необходимое количество клиентов до сбалансированности. 


Функция class_1_percent_samples принемает две переменные:
- target_data - массив с id и целевой переменной
- class_1_percent - процент класса 1 в результирующем массиве

In [647]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'date'
count_features = dict_spaces[feature_space]

In [648]:
# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

In [649]:
# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)
y_train_pd.head(4)

id  flag
id                    
1825800  1825800     0
2166483  2166483     0
2534345  2534345     0
1803283  1803283     0

In [650]:
# взглянем на сблансиорованность данных в y_train
y_train_pd['flag'].value_counts(normalize=True)

flag
0    0.964242
1    0.035758
Name: proportion, dtype: float64

In [651]:
# сбалансируем данные в y_train_pd
list_c1_percent_id = class_1_percent_samples(y_train_pd,0.5)
# list_c1_percent_features - список 'id' из y_train_pd соотвествующих  
# заданному проценту класса 1
len(list_c1_percent_id)

45860

In [652]:
# проверим сбалансированность полученного y_train
y_train_pd.loc[list_c1_percent_id]['flag'].value_counts(normalize=True)

flag
1    0.5
0    0.5
Name: proportion, dtype: float64

В отличие от данных в *transform_data_torow*, где модели показываеются последние N  
операций клиента, в данные в *transform_data_stat* сфомированы из различных статистических   
характеристик ряда определяющего клиентскую историю в банке. 

Соотвественно, если в данных *transform_data_torow* была сильная корреляция между признаками,  
то я не смог бы ее убрать, иначе потярется смысл "показать последовательный ряд в историии клиента".  
Признаки в *transform_data_stat* не имеют такой особенности. Поэтому, необходимо проанализировать  
данные в *transform_data_stat* и, в случае сильной коррреляции признаков, устранить ее.

In [653]:
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()
corr_matrix.shape

(137, 137)

In [654]:
# с помощью функции corr_transrom_to_power получим
# силу корреляции матрицы и список не коррелируемых признаков

# для начального анализа зададим порог силы корреляции, при котором признаки 
# будут отнесены к "сильно скоррелированными" равным 0.6
ncorr_matrix,list_ncorr_features,corr_power =corr_transform_to_force(corr_matrix,threshold=0.6)

# Выведем результаты преобразования
print('Исходное количество признаков: ', corr_matrix.shape[0])
print('Количество не коррелируемых признаков: ', len(list_ncorr_features))
# сила корреляции признаков
print('Отношение коррелируемых исходному количеству признаков (сила корреляции): ',corr_power)

Исходное количество признаков:  137
Количество не коррелируемых признаков:  42
Отношение коррелируемых исходному количеству признаков (сила корреляции):  0.693


In [655]:
# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']
# сформируем данные для проверики модели
# сформируем данные для анализа сбалансированности обучающих данных
X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()
y_train = pd.read_csv('target/target_train.csv')['flag']
X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()
y_valid = pd.read_csv('target/target_valid.csv')['flag']

In [656]:
# посмотрим на структуру данных в X_train_balanced
X_train_balanced.head(4)

f1    f2      f3      f4      f5      f6      f7   f8     f9  f10  \
id                                                                             
2335465  17.0  16.0   9.059   7.140   7.140  17.387   9.059  0.0  5.641  2.0   
390270    6.0  12.0  15.000  14.260  14.260  18.587  15.000  0.0  4.123  7.0   
2494034  14.0  15.0   9.714   8.242   8.242  16.484   9.714  0.0  4.832  2.0   
2018674  15.0  16.0   9.200   0.000   0.000  15.375   9.200  0.0  6.134  0.0   

         ...   f128  f129  f130  f131  f132  f133  f134  f135   f136  f137  
id       ...                                                                
2335465  ...  0.381   0.0   0.0   0.0   0.0   1.0   0.0  0.82  0.154   0.5  
390270   ...  0.500   0.0   0.0   0.5   1.0   1.0   0.0  1.00  0.300   0.5  
2494034  ...  0.258   0.0   0.0   0.0   0.0   1.0   0.0  0.93  0.071   0.5  
2018674  ...  0.249   0.0   0.0   0.0   0.0   1.0   0.0  0.93  0.067   0.5  

[4 rows x 137 columns]

In [657]:
# посмотрим на структуру данных в y_train_balanced
y_train_balanced.head(4)

id
2335465    1
390270     1
2494034    1
2018674    1
Name: flag, dtype: int64

In [658]:
# проверим что выборки действительно совпадают по id
X_train_balanced.index.to_list() == y_train_balanced.index.to_list()

True

##### <span style="color:MediumSlateBlue">Baseline обучение модели RandomForestClassifier</span>

In [659]:
# обучаем модель логистической регрессии
# чтобы модель пыталась найти связь во всех признаках
random_forest = RandomForestClassifier(random_state=42, n_jobs=-1)
random_forest.fit(X_train_balanced[list_ncorr_features],y_train_balanced)

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_rf__pred_proba = random_forest.predict_proba(X_train[list_ncorr_features])[:,1]
y_valid_rf_pred_proba = random_forest.predict_proba(X_valid[list_ncorr_features])[:,1]

# Делаем предсказание для валидационной выборки
y_valid_rf_pred = random_forest.predict(X_valid[list_ncorr_features])

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_rf__pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_rf_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_rf_pred))

# time: 17s

ROC AUC на обучающем наборе 0.975
ROC AUC на валидационном наборе 0.577
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.97      0.62      0.76     68747
           1       0.05      0.50      0.08      2503

    accuracy                           0.62     71250
   macro avg       0.51      0.56      0.42     71250
weighted avg       0.94      0.62      0.73     71250



##### <span style="color:MediumSlateBlue">Подбор гиперпараметров модели</span>

In [1672]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'date'
count_features = dict_spaces[feature_space]

# для работы функции corr_transform_to_force
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()

# настроим оптимизацию гипер параметров
def optuna_rf(trial):
  # задаем пространства поиска гиперпараметров
  # задаем пространства поиска гиперпараметров
  n_estimators = trial.suggest_int('n_estimators', 40, 100,step = 5)
  criterion = trial.suggest_categorical('criterion',['gini', 'entropy', 'log_loss'])
  max_depth = trial.suggest_int('max_depth', 10, 30,step = 1)
  min_samples_split = trial.suggest_int('min_samples_split', 5, 15,step = 1)
  min_samples_leaf = trial.suggest_int('min_samples_leaf', 5, 15,step = 1)
  max_features = trial.suggest_float('max_features',0.4,0.8)
  max_samples = trial.suggest_float('max_samples',0.4,0.8)
  class_0_weight = trial.suggest_float('class_0_weight',0.1,1)
  class_1_weight = trial.suggest_float('class_1_weight',0.1,1)
  threshold = trial.suggest_float('threshold',0.4,0.8)
  class_1_percent = trial.suggest_float('class_1_percent',0.01,0.5)
  random_state = trial.suggest_int('random_state', 1, 1000000)


  # создаем модель
  optuna_random_forest = RandomForestClassifier(
      n_estimators = n_estimators, 
      criterion = criterion,
      max_depth = max_depth,
      min_samples_split = min_samples_split,  
      min_samples_leaf = min_samples_leaf,
      max_features=max_features,
      max_samples=max_samples,
      class_weight={0:class_0_weight,1:class_1_weight},
      n_jobs=-1,
      random_state=42)

  # с помощью функции corr_transform_to_force получим
  # список не коррелируемых признаков
  list_ncorr_features = corr_transform_to_force(corr_matrix,threshold=threshold)[1]

  # сформируем данные для анализа сбалансированности обучающих данных
  X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
  y_train_pd = pd.read_csv('target/target_train.csv')

  # поготовим данные y_train_pd к работе с функцией class_1_percent_samples
  y_train_pd.set_index('id',drop=False,inplace=True)

  # подготовим данные для обучения модели
  # с помощью функции class_1_percent_samples зададим долю 
  # класса 1
  list_c1_percent_id = class_1_percent_samples(y_train_pd,class_1_percent,random_state=random_state)[:1000000]

  # подготовим данные для обучения
  X_train_balanced = X_train_pd.loc[list_c1_percent_id]
  y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']

  # освободим память от "тяжелых" и ненужных файлов
  del X_train_pd, y_train_pd
  gc.collect()

  # я не воспользовался параметром timeout метода optimize потому, что  
  # optimize отставливает поиск параметров, если время обучения 
  # превышает timeout. Мне нужно чтобы поиск параметров продолжился.
  try:
    # для модуля func_time_out упакуем обучение модели в функцию try_func
    def try_func():
            return optuna_random_forest.fit(X_train_balanced, y_train_balanced)
    # обучаем модель с ограничением по времени 10 минут (600 секунд)
    optuna_random_forest = func_timeout.func_timeout(600, try_func)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train_balanced, y_train_balanced
    gc.collect()

    # загружаем тестовые наборы
    # сформируем данные для анализа сбалансированности обучающих данных
    X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
    X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()[list_ncorr_features]
    y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
    y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()
    
    # делаем предсказание на обучающем и валидационном наборе
    #Считаем метрики для класса 1 добавляем их в список
    roc_train = metrics.roc_auc_score(y_train, optuna_random_forest.predict_proba(X_train)[:,1])
    roc_valid = metrics.roc_auc_score(y_valid, optuna_random_forest.predict_proba(X_valid)[:,1])
    f1_score = metrics.f1_score(y_valid, optuna_random_forest.predict(X_valid))
    recall_1 = metrics.recall_score(y_valid, optuna_random_forest.predict(X_valid),average=None,zero_division=0)[1]
    precision_1 = metrics.precision_score(y_valid, optuna_random_forest.predict(X_valid),average=None,zero_division=0)[1]

    # удаляем крупные файлы чтобы высвободить память 
    del X_train, X_valid, y_train, y_valid
    gc.collect()

  except func_timeout.FunctionTimedOut:
    # удаляем крупные файлы чтобы высвободить память 
    del X_train_balanced, y_train_balanced
    gc.collect()
    
    # фиксируем пустые значения метрик
    roc_train = 0
    roc_valid = 0
    f1_score = 0
    recall_1 = 0
    precision_1 = 0
    pass

  return roc_train, roc_valid, f1_score, recall_1, precision_1

In [1673]:
# cоздаем объект исследования
optuna_study_rf = optuna.create_study(study_name= 'RandomForestClassifier_'+feature_space+'_stat', 
                               directions=['maximize','maximize','maximize','maximize','maximize'], 
                               sampler=optuna.samplers.TPESampler(),
                               pruner='Hyperband',
                               storage='sqlite:///optuna_studies.db',
                               load_if_exists=True)
# на случай удаления 
# optuna.delete_study(study_name='RandomForestClassifier_'+feature_space+'_stat', storage='sqlite:///optuna_studies.db')

[I 2025-04-19 14:36:51,543] Using an existing study with name 'RandomForestClassifier_date_stat' instead of creating a new one.


In [662]:
# ищем лучшую комбинацию гиперпараметров n_trials раз
optuna_study_rf.optimize(optuna_rf, n_trials=300)

[I 2025-04-17 20:17:55,446] Trial 0 finished with values: [0.6548308293220231, 0.5899144454585898, 0.08310660400692554, 0.06711945665201757, 0.10909090909090909] and parameters: {'n_estimators': 50, 'criterion': 'entropy', 'max_depth': 10, 'min_samples_split': 5, 'min_samples_leaf': 13, 'max_features': 0.52000372738217, 'max_samples': 0.752710721716475, 'class_0_weight': 0.5130793120152063, 'class_1_weight': 0.3196547938026775, 'threshold': 0.4003396503216311, 'class_1_percent': 0.43091077534008015, 'random_state': 83982}.
[I 2025-04-17 20:17:59,897] Trial 1 finished with values: [0.6954220575362065, 0.59686536366987, 0.06804294870922527, 0.9988014382740711, 0.035221189067342916] and parameters: {'n_estimators': 55, 'criterion': 'entropy', 'max_depth': 12, 'min_samples_split': 14, 'min_samples_leaf': 14, 'max_features': 0.5146410845967917, 'max_samples': 0.4631172327739934, 'class_0_weight': 0.17737280459872234, 'class_1_weight': 0.9931016362903657, 'threshold': 0.4946057402105001, 'cl

In [1674]:
# из полученного результат соврмируем Data Frame
optuna_study_rf_pd = optuna_study_rf.trials_dataframe().dropna()
# переименуем столбы
optuna_study_rf_pd.rename(columns={
    'values_0': 'roc_train',
    'values_1': 'roc_valid',
    'values_2': 'f1_score',
    'values_3': 'recall_1',
    'values_4': 'precision_1'
},inplace=True)
optuna_study_rf_pd.tail()

number  roc_train  roc_valid  f1_score  recall_1  precision_1  \
295     295   0.970309   0.591669  0.003976  0.001998     0.416667   
296     296   0.895297   0.582829  0.015244  0.007990     0.165289   
297     297   0.921403   0.597791  0.084108  0.576508     0.045363   
298     298   0.769833   0.600100  0.067890  1.000000     0.035138   
299     299   0.743552   0.592799  0.068422  0.988813     0.035437   

                datetime_start          datetime_complete  \
295 2025-04-17 21:34:42.143899 2025-04-17 21:35:16.380205   
296 2025-04-17 21:35:16.385476 2025-04-17 21:35:30.386550   
297 2025-04-17 21:35:30.392453 2025-04-17 21:35:47.798362   
298 2025-04-17 21:35:47.803910 2025-04-17 21:35:59.301917   
299 2025-04-17 21:35:59.308373 2025-04-17 21:36:13.901642   

                  duration  params_class_0_weight  ...  params_criterion  \
295 0 days 00:00:34.236306               0.157354  ...           entropy   
296 0 days 00:00:14.001074               0.172195  ...           entropy   
297 0 days 00:00:17.405909               0.100581  ...           entropy   
298 0 days 00:00:11.498007               0.108070  ...           entropy   
299 0 days 00:00:14.593269               0.108486  ...           entropy   

     params_max_depth params_max_features  params_max_samples  \
295                24            0.544541            0.774766   
296                23            0.483149            0.640167   
297                24            0.472123            0.764511   
298                13            0.671041            0.761378   
299                11            0.695608            0.758918   

     params_min_samples_leaf  params_min_samples_split  params_n_estimators  \
295                       12                         7                   90   
296                       13                         5                   95   
297                       13                         5                   95   
298                       14                         5                   95   
299                       13                         5                   95   

     params_random_state  params_threshold     state  
295               383027          0.758348  COMPLETE  
296               336905          0.721188  COMPLETE  
297               612601          0.773438  COMPLETE  
298               649702          0.771773  COMPLETE  
299               689036          0.745632  COMPLETE  

[5 rows x 22 columns]

In [664]:
# покаждем статистику обучения
print('Максимальное значение метрики ROC AUC на валидационном наборе:',round(optuna_study_rf_pd['roc_valid'].max(),3))
print('Среднее значение метрики ROC AUC на валидационном наборе:',round(optuna_study_rf_pd['roc_valid'].mean(),3))
print('Максимальное значение метрики f1_score на валидационном наборе:',round(optuna_study_rf_pd['f1_score'].max(),3))
print('Среднее значение метрики f1_score на валидационном наборе:',round(optuna_study_rf_pd['f1_score'].mean(),3))
print('Максимальное значение метрики recall_1 на валидационном наборе:',round(optuna_study_rf_pd['recall_1'].max(),3))
print('Среднее значение метрики recall_1 на валидационном наборе:',round(optuna_study_rf_pd['recall_1'].mean(),3))
print('Максимальное значение метрики precision_1 на валидационном наборе:',round(optuna_study_rf_pd['precision_1'].max(),3))
print('Среднее значение метрики precision_1 на валидационном наборе:',round(optuna_study_rf_pd['precision_1'].mean(),3))

Максимальное значение метрики ROC AUC на валидационном наборе: 0.604
Среднее значение метрики ROC AUC на валидационном наборе: 0.594
Максимальное значение метрики f1_score на валидационном наборе: 0.105
Среднее значение метрики f1_score на валидационном наборе: 0.078
Максимальное значение метрики recall_1 на валидационном наборе: 1.0
Среднее значение метрики recall_1 на валидационном наборе: 0.278
Максимальное значение метрики precision_1 на валидационном наборе: 0.5
Среднее значение метрики precision_1 на валидационном наборе: 0.082


In [1676]:
# Построим зависимость метрик качества модели от number

fig = px.scatter(
    data_frame=optuna_study_rf_pd[(optuna_study_rf_pd['roc_valid']>=0.9999*optuna_study_rf_pd['roc_valid'].max())],
    x='number', #ось абсцисс
    y=['roc_valid','roc_train','precision_1','recall_1'], #ось ординат
)
fig.update_layout(
    title ={
        'text':'Зависимость качества модели от trials optuna', # Имя рабочей плоскости
        'font':{'size':35,'family':"Times New Roman"}, # размер и стиль написания имени рабочей плоскости
        'x':0.5, # Смешение имени по оси "x" на половину рабочей плоскости
        },
    height =800,# Высота рабочей плоскости
    width = 1350, # Ширина рабочей плоскости
    bargap=0.2, # Добавил расстояния между столбами гистограммы
    xaxis_title='trials optuna',
    yaxis_title='Величина параметра')
fig.update_xaxes(showspikes=True)
fig.update_yaxes(showspikes=True)

fig.show()

<span style="color:Blue">

Вывод:  

Их всех выбираем точку $number =77$.   
Не смотря на, то что в этой точке модель подает признаки переобучеености,  
в этой точке оптимальные значения метрик $recall_1$ и $precision_1$, а  
также относительно высокая метрика $ROC AUC$.   
Посмотрим каким значениям гиперпараметров соотвествует выбраннаяточка.

In [1677]:
# определим номер лучшге варианта
best_optuna_number = 77

# сформируем словарь лучших гипирпарметров RandomForestClassifier
best_param_rf = {
    'n_estimators' : int(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_n_estimators'].iloc[0]),
    'criterion': optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_criterion'].iloc[0],
    'max_depth' : int(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_max_depth'].iloc[0]),
    'min_samples_split': int(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_min_samples_split'].iloc[0]),
    'min_samples_leaf' : int(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_min_samples_leaf'].iloc[0]),
    'max_features': optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_max_features'].iloc[0],
    'max_samples' : optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_max_samples'].iloc[0],
    'class_weight' : {0:optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_class_0_weight'].iloc[0],
                      1:optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_class_1_weight'].iloc[0]}
    }

# определим перменные для лучших значений параметров
best_threshold = optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_threshold'].iloc[0]
best_class_1_percent = optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_class_1_percent'].iloc[0]
best_random_state = optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_random_state'].iloc[0]


# Выведем принятые наилучшие праметры
print('best n estimators:',best_param_rf['n_estimators'])
print('best criterion:',best_param_rf['criterion'])
print('best max depth:',best_param_rf['max_depth'])
print('best min samples split:',best_param_rf['min_samples_split'])
print('best min samples leaf:',best_param_rf['min_samples_leaf'])
print('best max features(%):',round(best_param_rf['max_features'],3))
print('best max samples(%):',round(best_param_rf['max_samples'],3))
print('best class 0 weight:',round(best_param_rf['class_weight'][0],3))
print('best class 1 weight:',round(best_param_rf['class_weight'][1],3))

print('best class 1 percent:',round(best_class_1_percent,3))
print('best threshold:',round(best_threshold,3))
print('best random state:', best_random_state)
print('time for best train:',round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['duration'].iloc[0].seconds/60),'minutes')

print()
print('ROC AUC на обучающем наборе:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['roc_train'].iloc[0],3))
print('ROC AUC на валидационном наборе:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['roc_valid'].iloc[0],3))
print('precision класса 1:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['precision_1'].iloc[0],3))
print('recall класса 1:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['recall_1'].iloc[0],3))

best n estimators: 95
best criterion: entropy
best max depth: 18
best min samples split: 6
best min samples leaf: 11
best max features(%): 0.747
best max samples(%): 0.628
best class 0 weight: 0.452
best class 1 weight: 0.769
best class 1 percent: 0.211
best threshold: 0.725
best random state: 835007
time for best train: 0 minutes

ROC AUC на обучающем наборе: 0.889
ROC AUC на валидационном наборе: 0.604
precision класса 1: 0.113
recall класса 1: 0.064


##### <span style="color:MediumSlateBlue">Обучение модели с лучшими параметрами</span>

In [1678]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'date'
count_features = dict_spaces[feature_space]

# для работы функции corr_transform_to_force
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()

# с помощью функции corr_transform_to_force получим
# список не коррелируемых признаков
list_ncorr_features = corr_transform_to_force(corr_matrix,threshold=best_threshold)[1]

# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
y_train_pd = pd.read_csv('target/target_train.csv')

# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)

# подготовим данные для обучения модели
# с помощью функции class_1_percent_samples зададим долю 
# класса 1
list_c1_percent_id = class_1_percent_samples(y_train_pd,best_class_1_percent,random_state=best_random_state)[:1000000]

# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']

# освободим память от "тяжелых" и ненужных файлов
del X_train_pd, y_train_pd
gc.collect()


# обучаем модель RandomForestClassifier с наилучшеми параметрами
random_forest = RandomForestClassifier(
        **best_param_rf,
        n_jobs=-1,
        random_state=42)
random_forest.fit(X_train_balanced, y_train_balanced)

# удаляем крупные файлы чтобы высвободить память 
del X_train_balanced, y_train_balanced
gc.collect()

# загружаем тестовые наборы
# сформируем данные для анализа сбалансированности обучающих данных
X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()[list_ncorr_features]
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_rf_pred_proba = random_forest.predict_proba(X_train)[:,1]
y_valid_rf_pred_proba = random_forest.predict_proba(X_valid)[:,1]

# Делаем предсказание для валидационной выборки
y_valid_rf_pred = random_forest.predict(X_valid)

# удаляем крупные файлы чтобы высвободить память 
del X_train, X_valid
gc.collect()

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_rf_pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_rf_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_rf_pred,zero_division=0))

# time: 5m 30s

ROC AUC на обучающем наборе 0.889
ROC AUC на валидационном наборе 0.604
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.97      0.98      0.97     68747
           1       0.11      0.06      0.08      2503

    accuracy                           0.95     71250
   macro avg       0.54      0.52      0.53     71250
weighted avg       0.94      0.95      0.94     71250



#### <span style="color:MediumBlue">Построение модели Gradient Boosting Classifier</span>

##### <span style="color:MediumSlateBlue">Формирование данных для обучения</span>

Анализ исходных данных, в частности target, показал что представленные данные   
имееют перекос: 96% клиентов у которых не случился дефолт (flag = 0),    
против 4 % - для которых произошел дефолт (flag = 1).  
С помощью функции class_1_percent_samples, сформируем сбаланисрованную выборку  
для обучения моделей.
За основу сбалансировных данных возьмем данные клиентов с дефолтом  
и к ним будем добирать необходимое количество клиентов до сбалансированности. 


Функция class_1_percent_samples принемает две переменные:
- target_data - массив с id и целевой переменной
- class_1_percent - процент класса 1 в результирующем массиве

In [680]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'date'
count_features = dict_spaces[feature_space]

In [681]:
# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

In [682]:
# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)
y_train_pd.head(4)

id  flag
id                    
1825800  1825800     0
2166483  2166483     0
2534345  2534345     0
1803283  1803283     0

In [683]:
# взглянем на сблансиорованность данных в y_train
y_train_pd['flag'].value_counts(normalize=True)

flag
0    0.964242
1    0.035758
Name: proportion, dtype: float64

In [684]:
# сбалансируем данные в y_train_pd
list_c1_percent_id = class_1_percent_samples(y_train_pd,0.5)
# list_c1_percent_features - список 'id' из y_train_pd соотвествующих  
# заданному проценту класса 1
len(list_c1_percent_id)

45860

In [685]:
# проверим сбалансированность полученного y_train
y_train_pd.loc[list_c1_percent_id]['flag'].value_counts(normalize=True)

flag
1    0.5
0    0.5
Name: proportion, dtype: float64

В отличие от данных в *transform_data_torow*, где модели показываеются последние N  
операций клиента, в данные в *transform_data_stat* сфомированы из различных статистических   
характеристик ряда определяющего клиентскую историю в банке. 

Соотвественно, если в данных *transform_data_torow* была сильная корреляция между признаками,  
то я не смог бы ее убрать, иначе потярется смысл "показать последовательный ряд в историии клиента".  
Признаки в *transform_data_stat* не имеют такой особенности. Поэтому, необходимо проанализировать  
данные в *transform_data_stat* и, в случае сильной коррреляции признаков, устранить ее.

In [686]:
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()
corr_matrix.shape

(137, 137)

In [687]:
# с помощью функции corr_transrom_to_power получим
# силу корреляции матрицы и список не коррелируемых признаков

# для начального анализа зададим порог силы корреляции, при котором признаки 
# будут отнесены к "сильно скоррелированными" равным 0.6
ncorr_matrix,list_ncorr_features,corr_power =corr_transform_to_force(corr_matrix,threshold=0.6)

# Выведем результаты преобразования
print('Исходное количество признаков: ', corr_matrix.shape[0])
print('Количество не коррелируемых признаков: ', len(list_ncorr_features))
# сила корреляции признаков
print('Отношение коррелируемых исходному количеству признаков (сила корреляции): ',corr_power)

Исходное количество признаков:  137
Количество не коррелируемых признаков:  42
Отношение коррелируемых исходному количеству признаков (сила корреляции):  0.693


In [688]:
# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']
# сформируем данные для проверики модели
# сформируем данные для анализа сбалансированности обучающих данных
X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()
y_train = pd.read_csv('target/target_train.csv')['flag']
X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()
y_valid = pd.read_csv('target/target_valid.csv')['flag']

In [689]:
# посмотрим на структуру данных в X_train_balanced
X_train_balanced.head(4)

f1    f2      f3      f4      f5      f6      f7   f8     f9  f10  \
id                                                                             
2335465  17.0  16.0   9.059   7.140   7.140  17.387   9.059  0.0  5.641  2.0   
390270    6.0  12.0  15.000  14.260  14.260  18.587  15.000  0.0  4.123  7.0   
2494034  14.0  15.0   9.714   8.242   8.242  16.484   9.714  0.0  4.832  2.0   
2018674  15.0  16.0   9.200   0.000   0.000  15.375   9.200  0.0  6.134  0.0   

         ...   f128  f129  f130  f131  f132  f133  f134  f135   f136  f137  
id       ...                                                                
2335465  ...  0.381   0.0   0.0   0.0   0.0   1.0   0.0  0.82  0.154   0.5  
390270   ...  0.500   0.0   0.0   0.5   1.0   1.0   0.0  1.00  0.300   0.5  
2494034  ...  0.258   0.0   0.0   0.0   0.0   1.0   0.0  0.93  0.071   0.5  
2018674  ...  0.249   0.0   0.0   0.0   0.0   1.0   0.0  0.93  0.067   0.5  

[4 rows x 137 columns]

In [690]:
# посмотрим на структуру данных в y_train_balanced
y_train_balanced.head(4)

id
2335465    1
390270     1
2494034    1
2018674    1
Name: flag, dtype: int64

In [691]:
# проверим что выборки действительно совпадают по id
X_train_balanced.index.to_list() == y_train_balanced.index.to_list()

True

##### <span style="color:MediumSlateBlue">Baseline обучение модели Hist Gradient Boosting Classifier</span>

In [692]:
# обучаем модель Gradient Boosting Classifier
gradient_boosting = HistGradientBoostingClassifier(random_state=42)
gradient_boosting.fit(X_train_balanced[list_ncorr_features],y_train_balanced)

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_rf__pred_proba = gradient_boosting.predict_proba(X_train[list_ncorr_features])[:,1]
y_valid_rf_pred_proba = gradient_boosting.predict_proba(X_valid[list_ncorr_features])[:,1]

# Делаем предсказание для валидационной выборки
y_valid_rf_pred = gradient_boosting.predict(X_valid[list_ncorr_features])

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_rf__pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_rf_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_rf_pred))

# time: 30s

ROC AUC на обучающем наборе 0.651
ROC AUC на валидационном наборе 0.607
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.97      0.62      0.76     68747
           1       0.05      0.53      0.09      2503

    accuracy                           0.62     71250
   macro avg       0.51      0.58      0.42     71250
weighted avg       0.94      0.62      0.74     71250



##### <span style="color:MediumSlateBlue">Подбор гиперпараметров модели</span>

In [1679]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'date'
count_features = dict_spaces[feature_space]

# для работы функции corr_transform_to_force
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()

# настроим оптимизацию гипер параметров
def optuna_hgbc(trial):
  # задаем пространства поиска гиперпараметров
  learning_rate = trial.suggest_float('learning_rate',0.01,0.1)
  max_iter = trial.suggest_int('max_iter', 150, 250,step = 1)
  max_leaf_nodes = trial.suggest_int('max_leaf_nodes', 2, 60,step = 1)
  max_depth = trial.suggest_int('max_depth', 1, 10,step = 1)
  min_samples_leaf = trial.suggest_int('min_samples_leaf', 1, 60,step = 1)
  max_features = trial.suggest_float('max_features',0.6,1)
  l2_regularization = trial.suggest_float('l2_regularization',0.01,1)
  class_0_weight = trial.suggest_float('class_0_weight',0.01,1)
  class_1_weight = trial.suggest_float('class_1_weight',0.5,1)
  threshold = trial.suggest_float('threshold',0.7,1)
  class_1_percent = trial.suggest_float('class_1_percent',0.01,0.25)
  random_state = trial.suggest_int('random_state', 1, 1000000)

  # создаем модель
  optuna_gradient_boosting = HistGradientBoostingClassifier(
      learning_rate= learning_rate,
      max_iter = max_iter,
      max_leaf_nodes =max_leaf_nodes,
      max_depth = max_depth,
      min_samples_leaf = min_samples_leaf,
      max_features=max_features,
      l2_regularization = l2_regularization,
      class_weight={0:class_0_weight,1:class_1_weight},
      random_state=42)

  # с помощью функции corr_transform_to_force получим
  # список не коррелируемых признаков
  list_ncorr_features = corr_transform_to_force(corr_matrix,threshold=threshold)[1]

  # сформируем данные для анализа сбалансированности обучающих данных
  X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
  y_train_pd = pd.read_csv('target/target_train.csv')

  # поготовим данные y_train_pd к работе с функцией class_1_percent_samples
  y_train_pd.set_index('id',drop=False,inplace=True)

  # подготовим данные для обучения модели
  # с помощью функции class_1_percent_samples зададим долю 
  # класса 1
  list_c1_percent_id = class_1_percent_samples(y_train_pd,class_1_percent,random_state=random_state)[:1000000]

  # подготовим данные для обучения
  X_train_balanced = X_train_pd.loc[list_c1_percent_id]
  y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']

  # освободим память от "тяжелых" и ненужных файлов
  del X_train_pd, y_train_pd
  gc.collect()

  # я не воспользовался параметром timeout метода optimize потому, что  
  # optimize отставливает поиск параметров, если время обучения 
  # превышает timeout. Мне нужно чтобы поиск параметров продолжился.
  try:
    # для модуля func_time_out упакуем обучение модели в функцию try_func
    def try_func():
            return optuna_gradient_boosting.fit(X_train_balanced,y_train_balanced)
    # обучаем модель с ограничением по времени 10 минут (600 секунд)
    optuna_gradient_boosting = func_timeout.func_timeout(600, try_func)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train_balanced, y_train_balanced
    gc.collect()

        # загружаем тестовые наборы
    # сформируем данные для анализа сбалансированности обучающих данных
    X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
    X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()[list_ncorr_features]
    y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
    y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()
    
    # делаем предсказание на обучающем и валидационном наборе и считаем метрики
    roc_train = metrics.roc_auc_score(y_train, optuna_gradient_boosting.predict_proba(X_train)[:,1])
    roc_valid = metrics.roc_auc_score(y_valid, optuna_gradient_boosting.predict_proba(X_valid)[:,1])
    f1_score = metrics.f1_score(y_valid, optuna_gradient_boosting.predict(X_valid))
    recall_1 = metrics.recall_score(y_valid, optuna_gradient_boosting.predict(X_valid),average=None,zero_division=0)[1]
    precision_1 = metrics.precision_score(y_valid, optuna_gradient_boosting.predict(X_valid),average=None,zero_division=0)[1]


    # удаляем крупные файлы чтобы высвободить память 
    del X_train, X_valid, y_train, y_valid
    gc.collect()

  except func_timeout.FunctionTimedOut:
    # удаляем крупные файлы чтобы высвободить память 
    del X_train_balanced, y_train_balanced
    gc.collect()
    
    # фиксируем пустые значения метрик
    roc_train = 0
    roc_valid = 0
    f1_score = 0
    recall_1 = 0
    precision_1 = 0
    pass

  return roc_train, roc_valid, f1_score, recall_1, precision_1

In [1680]:
# cоздаем объект исследования
# чтобы модель не переобучалась минимизируем roc_train 
# и максимизируем roc_valid
optuna_study_hgbc = optuna.create_study(study_name='HistGradientBoostingClassifier_'+feature_space+'_stat', 
                               directions=['maximize','maximize','maximize','maximize','maximize'], 
                               sampler=optuna.samplers.TPESampler(),
                               pruner='Hyperband',
                               storage='sqlite:///optuna_studies.db',
                               load_if_exists=True)

# ну случай удаления обучения
# optuna.delete_study(study_name='HistGradientBoostingClassifier'+feature_space+'_stat', storage='sqlite:///optuna_studies.db')

[I 2025-04-19 14:40:07,603] Using an existing study with name 'HistGradientBoostingClassifier_date_stat' instead of creating a new one.


In [695]:
# ищем лучшую комбинацию гиперпараметров n_trials раз
optuna_study_hgbc.optimize(optuna_hgbc, n_trials=300)

[I 2025-04-17 21:36:50,126] Trial 0 finished with values: [0.70228911418146, 0.6093688519272675, 0.00933852140077821, 0.004794246903715541, 0.1791044776119403] and parameters: {'learning_rate': 0.0832455643098909, 'max_iter': 245, 'max_leaf_nodes': 55, 'max_depth': 6, 'min_samples_leaf': 7, 'max_features': 0.712879607463318, 'l2_regularization': 0.08342282561192019, 'class_0_weight': 0.7190939416939984, 'class_1_weight': 0.5860232616573686, 'threshold': 0.7806645275011727, 'class_1_percent': 0.1667373075950276, 'random_state': 403828}.
[I 2025-04-17 21:36:58,532] Trial 1 finished with values: [0.6853863473352692, 0.618393006286764, 0.0007974481658692185, 0.00039952057530962844, 0.2] and parameters: {'learning_rate': 0.07147672361975342, 'max_iter': 221, 'max_leaf_nodes': 31, 'max_depth': 8, 'min_samples_leaf': 27, 'max_features': 0.7579694802126229, 'l2_regularization': 0.4174006276031334, 'class_0_weight': 0.8351652576507594, 'class_1_weight': 0.9267085861587127, 'threshold': 0.829449

In [1681]:
# из полученного результат соврмируем Data Frame
optuna_study_hgbc_pd = optuna_study_hgbc.trials_dataframe()
# переименуем столбы
optuna_study_hgbc_pd.rename(columns={
    'values_0': 'roc_train',
    'values_1': 'roc_valid',
    'values_2': 'f1_score',
    'values_3': 'recall_1',
    'values_4': 'precision_1'
},inplace=True)
optuna_study_hgbc_pd.tail(5)

number  roc_train  roc_valid  f1_score  recall_1  precision_1  \
295     295   0.713930   0.621968  0.103862  0.352377     0.060907   
296     296   0.711622   0.620197  0.104078  0.121854     0.090828   
297     297   0.708882   0.619517  0.105686  0.136636     0.086168   
298     298   0.711125   0.618520  0.101514  0.384339     0.058480   
299     299   0.690820   0.617815  0.106297  0.285258     0.065319   

                datetime_start          datetime_complete  \
295 2025-04-17 22:23:44.409127 2025-04-17 22:23:58.082020   
296 2025-04-17 22:23:58.087691 2025-04-17 22:24:11.198106   
297 2025-04-17 22:24:11.204619 2025-04-17 22:24:25.423743   
298 2025-04-17 22:24:25.428907 2025-04-17 22:24:38.643494   
299 2025-04-17 22:24:38.649825 2025-04-17 22:24:51.365679   

                  duration  params_class_0_weight  ...  \
295 0 days 00:00:13.672893               0.196556  ...   
296 0 days 00:00:13.110415               0.251154  ...   
297 0 days 00:00:14.219124               0.307590  ...   
298 0 days 00:00:13.214587               0.189959  ...   
299 0 days 00:00:12.715854               0.165213  ...   

     params_l2_regularization  params_learning_rate  params_max_depth  \
295                  0.868295              0.045216                 8   
296                  0.852370              0.051223                 8   
297                  0.827339              0.040100                 8   
298                  0.889285              0.047917                 8   
299                  0.801842              0.044168                 8   

     params_max_features  params_max_iter  params_max_leaf_nodes  \
295             0.921530              163                     58   
296             0.908982              167                     53   
297             0.943083              165                     50   
298             0.915415              168                     55   
299             0.895670              160                     51   

     params_min_samples_leaf  params_random_state  params_threshold     state  
295                       36               930037          0.881655  COMPLETE  
296                       41               971367          0.868185  COMPLETE  
297                       38               901626          0.875031  COMPLETE  
298                       40               946694          0.884098  COMPLETE  
299                       42               999363          0.865028  COMPLETE  

[5 rows x 22 columns]

In [1682]:
# покаждем статистику обучения
print('Максимальное значение метрики ROC AUC на валидационном наборе:',round(optuna_study_hgbc_pd['roc_valid'].max(),3))
print('Среднее значение метрики ROC AUC на валидационном наборе:',round(optuna_study_hgbc_pd['roc_valid'].mean(),3))
print('Максимальное значение метрики f1_score на валидационном наборе:',round(optuna_study_hgbc_pd['f1_score'].max(),3))
print('Среднее значение метрики f1_score на валидационном наборе:',round(optuna_study_hgbc_pd['f1_score'].mean(),3))
print('Максимальное значение метрики recall_1 на валидационном наборе:',round(optuna_study_hgbc_pd['recall_1'].max(),3))
print('Среднее значение метрики recall_1 на валидационном наборе:',round(optuna_study_hgbc_pd['recall_1'].mean(),3))
print('Максимальное значение метрики precision_1 на валидационном наборе:',round(optuna_study_hgbc_pd['precision_1'].max(),3))
print('Среднее значение метрики precision_1 на валидационном наборе:',round(optuna_study_hgbc_pd['precision_1'].mean(),3))

Максимальное значение метрики ROC AUC на валидационном наборе: 0.623
Среднее значение метрики ROC AUC на валидационном наборе: 0.616
Максимальное значение метрики f1_score на валидационном наборе: 0.115
Среднее значение метрики f1_score на валидационном наборе: 0.074
Максимальное значение метрики recall_1 на валидационном наборе: 1.0
Среднее значение метрики recall_1 на валидационном наборе: 0.301
Максимальное значение метрики precision_1 на валидационном наборе: 1.0
Среднее значение метрики precision_1 на валидационном наборе: 0.088


In [1685]:
# Построим зависимость метрик качества модели от number

fig = px.scatter(
    data_frame=optuna_study_hgbc_pd[(optuna_study_hgbc_pd['roc_valid']>0.999*optuna_study_hgbc_pd['roc_valid'].max())],
    x='number', #ось абсцисс
    y=['roc_train','roc_valid','recall_1','precision_1'], #ось ординат
)
fig.update_layout(
    title ={
        'text':'Зависимость качества модели от trials optuna', # Имя рабочей плоскости
        'font':{'size':35,'family':"Times New Roman"}, # размер и стиль написания имени рабочей плоскости
        'x':0.5, # Смешение имени по оси "x" на половину рабочей плоскости
        },
    height =800,# Высота рабочей плоскости
    width = 1350, # Ширина рабочей плоскости
    bargap=0.2, # Добавил расстояния между столбами гистограммы
    xaxis_title='trials optuna',
    yaxis_title='Величина параметра')
fig.update_xaxes(showspikes=True)
fig.update_yaxes(showspikes=True)

fig.show()

<span style="color:Blue">

Вывод:  

Их всех выбираем точку $number =288$.   
В этой точке оптимальные значения метрик $recall_1$ и $precision_1$, а  
также относительно высокая метрика $ROC AUC$.   
Посмотрим каким значениям гиперпараметров соотвествует выбранная точка.

In [1686]:
# определим номер лучшге варианта
best_optuna_number = 288

# сформируем словарь лучших гипирпарметров HistGradientBoostingClassifier
best_param_hgbc = {
    'learning_rate' : optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_learning_rate'].iloc[0],
    'max_iter' : optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_max_iter'].iloc[0],
    'max_leaf_nodes' : optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_max_leaf_nodes'].iloc[0],
    'max_depth' : optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_max_depth'].iloc[0],
    'min_samples_leaf' : optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_min_samples_leaf'].iloc[0],
    'max_features' : optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_max_features'].iloc[0],
    'l2_regularization' : optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_l2_regularization'].iloc[0],
    'class_weight' : {0: optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_class_0_weight'].iloc[0],
                      1: optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_class_1_weight'].iloc[0],}
    }

# определим перменные для лучших значений параметров
best_threshold = optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_threshold'].iloc[0]
best_class_1_percent = optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_class_1_percent'].iloc[0]
best_random_state = optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_random_state'].iloc[0]


# Выведем принятые наилучшие параметры
print('best learning rate:',round(best_param_hgbc['learning_rate'],3))
print('best max iter:',best_param_hgbc['max_iter'])
print('best max leaf nodes:',best_param_hgbc['max_leaf_nodes'])
print('best max depth:',best_param_hgbc['max_depth'])
print('best min samples leaf:',best_param_hgbc['min_samples_leaf'])
print('best max features:',round(best_param_hgbc['max_features'],3))
print('best l2 regularization:',round(best_param_hgbc['l2_regularization'],3))
print('best class 0 weight:',round(best_param_hgbc['class_weight'][0],3))
print('best class 1 weight:',round(best_param_hgbc['class_weight'][1],3))

print('best class 1 percent:',round(best_class_1_percent,3))
print('best threshold:',round(best_threshold,3))
print('time for best train:',round(optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['duration'].iloc[0].seconds/60),'minutes')

print()
print('ROC AUC на обучающем наборе:', round(optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['roc_train'].iloc[0],3))
print('ROC AUC на валидационном наборе:', round(optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['roc_valid'].iloc[0],3))
print('precision класса 1:', round(optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['precision_1'].iloc[0],3))
print('recall класса 1:', round(optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['recall_1'].iloc[0],3))

best learning rate: 0.05
best max iter: 165
best max leaf nodes: 51
best max depth: 8
best min samples leaf: 38
best max features: 0.938
best l2 regularization: 0.857
best class 0 weight: 0.226
best class 1 weight: 0.8
best class 1 percent: 0.147
best threshold: 0.881
time for best train: 0 minutes

ROC AUC на обучающем наборе: 0.714
ROC AUC на валидационном наборе: 0.623
precision класса 1: 0.084
recall класса 1: 0.163


##### <span style="color:MediumSlateBlue">Обучение модели с лучшими параметрами</span>

In [1687]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'date'
count_features = dict_spaces[feature_space]

# для работы функции corr_transform_to_force
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()

# с помощью функции corr_transform_to_force получим
# список не коррелируемых признаков
list_ncorr_features = corr_transform_to_force(corr_matrix,threshold=best_threshold)[1]

# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
y_train_pd = pd.read_csv('target/target_train.csv')

# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)

# подготовим данные для обучения модели
# с помощью функции class_1_percent_samples зададим долю 
# класса 1
list_c1_percent_id = class_1_percent_samples(y_train_pd,best_class_1_percent,random_state=best_random_state)[:1000000]

# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']

# освободим память от "тяжелых" и ненужных файлов
del X_train_pd, y_train_pd
gc.collect()

# обучаем модель HistGradientBoostingClassifier с наилучшеми параметрами
gradient_boosting = HistGradientBoostingClassifier(
        **best_param_hgbc,
        random_state=42)
gradient_boosting.fit(X_train_balanced,y_train_balanced)

# удаляем крупные файлы чтобы высвободить память 
del X_train_balanced, y_train_balanced
gc.collect()

# сформируем данные для анализа сбалансированности обучающих данных
X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()[list_ncorr_features]
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

# делаем предсказание на обучающем и валидационном наборе и считаем метрики
y_train_gb_pred_proba = gradient_boosting.predict_proba(X_train)[:,1]
y_valid_gb_pred_proba = gradient_boosting.predict_proba(X_valid)[:,1]
y_valid_gb_pred = gradient_boosting.predict(X_valid)

# удаляем крупные файлы чтобы высвободить память 
del X_train, X_valid
gc.collect()

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_gb_pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_gb_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_gb_pred,zero_division=0))

# time: 1m 40s

ROC AUC на обучающем наборе 0.714
ROC AUC на валидационном наборе 0.623
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.97      0.93      0.95     68747
           1       0.08      0.16      0.11      2503

    accuracy                           0.91     71250
   macro avg       0.53      0.55      0.53     71250
weighted avg       0.94      0.91      0.92     71250



### <span style="color:RoyalBlue">Построение модели на сбалансированных данных подпрострнства late stat</span>

#### <span style="color:MediumBlue">Построение модели Logistic Regression</span>

##### <span style="color:MediumSlateBlue">Формирование данных для обучения</span>

Анализ исходных данных, в частности target, показал что представленные данные   
имееют перекос: 96% клиентов у которых не случился дефолт (flag = 0),    
против 4 % - для которых произошел дефолт (flag = 1).  
С помощью функции class_1_percent_samples, сформируем сбаланисрованную выборку  
для обучения моделей.
За основу сбалансировных данных возьмем данные клиентов с дефолтом  
и к ним будем добирать необходимое количество клиентов до сбалансированности. 


Функция class_1_percent_samples принемает две переменные:
- target_data - массив с id и целевой переменной
- class_1_percent - процент класса 1 в результирующем массиве

In [714]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'late'
count_features = dict_spaces[feature_space]

In [715]:
# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

In [716]:
# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)
y_train_pd.head(4)

id  flag
id                    
1825800  1825800     0
2166483  2166483     0
2534345  2534345     0
1803283  1803283     0

In [717]:
# взглянем на сблансиорованность данных в y_train
y_train_pd['flag'].value_counts(normalize=True)

flag
0    0.964242
1    0.035758
Name: proportion, dtype: float64

In [718]:
# сбалансируем данные в y_train_pd
list_c1_percent_id = class_1_percent_samples(y_train_pd,0.5)
# list_c1_percent_features - список 'id' из y_train_pd соотвествующих  
# заданному проценту класса 1
len(list_c1_percent_id)

45860

In [719]:
# проверим сбалансированность полученного y_train
y_train_pd.loc[list_c1_percent_id]['flag'].value_counts(normalize=True)

flag
1    0.5
0    0.5
Name: proportion, dtype: float64

В отличие от данных в *transform_data_torow*, где модели показываеются последние N  
операций клиента, в данные в *transform_data_stat* сфомированы из различных статистических   
характеристик ряда определяющего клиентскую историю в банке. 

Соотвественно, если в данных *transform_data_torow* была сильная корреляция между признаками,  
то я не смог бы ее убрать, иначе потярется смысл "показать последовательный ряд в историии клиента".  
Признаки в *transform_data_stat* не имеют такой особенности. Поэтому, необходимо проанализировать  
данные в *transform_data_stat* и, в случае сильной коррреляции признаков, устранить ее.

In [720]:
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()
corr_matrix.shape

(205, 205)

In [721]:
# с помощью функции corr_transrom_to_power получим
# силу корреляции матрицы и список не коррелируемых признаков

# для начального анализа зададим порог силы корреляции, при котором признаки 
# будут отнесены к "сильно скоррелированными" равным 0.6
ncorr_matrix,list_ncorr_features,corr_power =corr_transform_to_force(corr_matrix,threshold=0.6)

# Выведем результаты преобразования
print('Исходное количество признаков: ', corr_matrix.shape[0])
print('Количество не коррелируемых признаков: ', len(list_ncorr_features))
# сила корреляции признаков
print('Отношение коррелируемых исходному количеству признаков (сила корреляции): ',corr_power)

Исходное количество признаков:  205
Количество не коррелируемых признаков:  67
Отношение коррелируемых исходному количеству признаков (сила корреляции):  0.673


In [722]:
# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']
# сформируем данные для проверики модели
# сформируем данные для анализа сбалансированности обучающих данных
X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()
y_train = pd.read_csv('target/target_train.csv')['flag']
X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()
y_valid = pd.read_csv('target/target_valid.csv')['flag']

In [723]:
# посмотрим на структуру данных в X_train_balanced
X_train_balanced.head(4)

f1   f2   f3   f4   f5   f6   f7   f8   f9  f10  ...   f196  f197  \
id                                                          ...                
2335465  17.0  0.0  6.0  6.0  6.0  6.0  6.0  0.0  0.0  6.0  ...  0.000   2.0   
390270    6.0  0.0  6.0  6.0  6.0  6.0  6.0  0.0  0.0  6.0  ...  0.000   2.0   
2494034  14.0  0.0  6.0  6.0  6.0  6.0  6.0  0.0  0.0  6.0  ...  0.000   2.0   
2018674  15.0  0.0  6.0  6.0  6.0  6.0  6.0  0.0  0.0  6.0  ...  0.249   2.0   

         f198  f199  f200  f201  f202  f203   f204  f205  
id                                                        
2335465   2.0   2.0   2.0   2.0   2.0  1.00  0.000   2.0  
390270    2.0   2.0   2.0   2.0   2.0  1.00  0.000   2.0  
2494034   2.0   2.0   2.0   2.0   2.0  1.00  0.000   2.0  
2018674   2.0   2.0   2.0   3.0   2.0  0.93  0.067   2.5  

[4 rows x 205 columns]

In [724]:
# посмотрим на структуру данных в y_train_balanced
y_train_balanced.head(4)

id
2335465    1
390270     1
2494034    1
2018674    1
Name: flag, dtype: int64

In [725]:
# проверим что выборки действительно совпадают по id
X_train_balanced.index.to_list() == y_train_balanced.index.to_list()

True

##### <span style="color:MediumSlateBlue">Baseline обучение модели LogisticRegression</span>

In [726]:
# обучаем модель логистической регрессии
logistic_regression = linear_model.LogisticRegression(random_state=42, max_iter=10000)
logistic_regression.fit(X_train_balanced[list_ncorr_features],y_train_balanced)

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_LR_pred_proba = logistic_regression.predict_proba(X_train[list_ncorr_features])[:,1]
y_valid_LR_pred_proba = logistic_regression.predict_proba(X_valid[list_ncorr_features])[:,1]

# Делаем предсказание для валидационной выборки
y_valid_LR_pred = logistic_regression.predict(X_valid[list_ncorr_features])

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_LR_pred_proba),3))
print('ROC AUC на тестовом наборе', round(metrics.roc_auc_score(y_valid, y_valid_LR_pred_proba),3))

print('Основные метрики на тестовом наборе:')
print(metrics.classification_report(y_valid,y_valid_LR_pred))

# time: 3m 5s

ROC AUC на обучающем наборе 0.613
ROC AUC на тестовом наборе 0.617
Основные метрики на тестовом наборе:
              precision    recall  f1-score   support

           0       0.98      0.56      0.71     68747
           1       0.05      0.61      0.09      2503

    accuracy                           0.56     71250
   macro avg       0.51      0.59      0.40     71250
weighted avg       0.94      0.56      0.69     71250



##### <span style="color:MediumSlateBlue">Анализ влияния scaler преобразования на качество и скорость схождения модели</span>

In [727]:
# формируем список из необходимых scaler
scalers = [MinMaxScaler(),RobustScaler() ,StandardScaler()]

# сформируем списко для заполнения данными результатов анализа
scalers_data = []

# установим ограничение на время обучения модели в 600 секунд (10 минут)
time_out = 600

for scaler in scalers:
        # для того чтобы следить за выполнением цикла введем индикатор
        print('current scaler: ', scaler)

         # сформируем список для заполнения данными текушего scaler
        current_scaler_data = [scaler]
        
        # выполним scaler преобразование
        X_train_s_balanced = scaler.fit_transform(X_train_balanced[list_ncorr_features])
        X_train_s = scaler.transform(X_train[list_ncorr_features])
        X_valid_s = scaler.transform(X_valid[list_ncorr_features])

        try:
                # для модуля func_time_out упакуем обучение модели в функцию try_func
                def try_func():
                        logistic_regression = linear_model.LogisticRegression(random_state=42, max_iter=10000)
                        return logistic_regression.fit(X_train_s_balanced,y_train_balanced)
                    
                # фиксируем время начала
                start_time = time.time()
                
                # запускаем обучение модели с ограничением по времени
                logistic_regression = func_timeout.func_timeout(time_out, try_func)
                
                # фиксируем время окончания обучения
                end_time = time.time()
                
                # запишем время обучения модели
                current_scaler_data.append(round(end_time-start_time))

                # Делаем предсказание для обучающей и валидационной выборки
                y_valid_lr_pred = logistic_regression.predict(X_valid_s)
                
                # для метрик ROC AUC делаем предсказание модели для обучающей и валидационной выборки  
                # в виде вероятности принадлежности к классу 1 
                y_train_lr_pred_proba = logistic_regression.predict_proba(X_train_s)[:,1]
                y_valid_lr_pred_proba = logistic_regression.predict_proba(X_valid_s)[:,1]

                #Считаем метрики ROC AUC yна обуающем и валидационном наборе и добавляем их в спискок
                current_scaler_data.append(round(metrics.roc_auc_score(y_train, y_train_lr_pred_proba),3))
                current_scaler_data.append(round(metrics.roc_auc_score(y_valid, y_valid_lr_pred_proba),3))

                #Считаем метрики для класса 0 на валидационном наборе и добавляем их в список
                current_scaler_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))
                current_scaler_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))


                #Считаем метрики для класса 1 на валидационном набопе и добавляем их в список
                current_scaler_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))
                current_scaler_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))

                # добавляем полученные данные в список scalers_data
                scalers_data.append(current_scaler_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                scaler_pd =pd.DataFrame(
                        columns=['scaler','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = scalers_data)
                # сохраняем dataframe
                scaler_pd.to_csv('data_recovery/scaler_pd.csv',index=False)
               
                # очистим output от прошедшей итерации
                clear_output()

        except func_timeout.FunctionTimedOut:
                # если время обучения привышает лимит
                # запишем в current_scaler_data соотвествующую данные
                current_scaler_data = [scaler,'>30m',0,0,0,0,0,0]
                # добавляем полученные данные в список scalers_data
                scalers_data.append(current_scaler_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                scaler_pd =pd.DataFrame(
                        columns=['scaler','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = scalers_data)
                # сохраняем dataframe
                scaler_pd.to_csv('data_recovery/scaler_pd.csv',index=False)
                
                # очистим output от прошедшей итерации
                clear_output()
                # переходим к следующему scaler
                pass
# очистим output
clear_output()

# сформируем данные соотвествующие лучщему ROC AUC на валидацинном наборе
best_roc_valid_data = scaler_pd[scaler_pd['roc_valid']==scaler_pd['roc_valid'].max()]

# выведем лучший результат на валидационном наборе
print('result:')
print('best scaler on valid:',best_roc_valid_data.iloc[0]['scaler'])
print('ROC AUC on train:', best_roc_valid_data.iloc[0]['roc_train'])
print('ROC AUC on valid:', best_roc_valid_data.iloc[0]['roc_valid'])
print('Time fit for best scaler:', best_roc_valid_data.iloc[0]['time_fit'],' seconds')

# выведем полученный dataframe
scaler_pd

# time: 

result:
best scaler on valid: MinMaxScaler()
ROC AUC on train: 0.613
ROC AUC on valid: 0.617
Time fit for best scaler: 0  seconds


scaler  time_fit  roc_train  roc_valid  recall_0  precision_0  \
0    MinMaxScaler()         0      0.613      0.617     0.558        0.975   
1    RobustScaler()         1      0.613      0.617     0.559        0.975   
2  StandardScaler()         0      0.613      0.617     0.560        0.975   

   recall_1  precision_1  
0     0.613        0.048  
1     0.611        0.048  
2     0.610        0.048

##### <span style="color:MediumSlateBlue"> Анализ влияния solver оптимизатора на качество и скорость обучения модели</span>

Проверим качество и скорость сходимости модели при разных solver  
Проверку осуществим через цикл  
Чтобы модель не сходилась бесконечно с помощью модуля func_timeout  
поставим ограничение времени схождения в 10 минут

In [728]:
# подготовим данные для обучения модели

# обьявим scaler
scaler = StandardScaler()
# выполним scaler преобразование
X_train_s_balanced = scaler.fit_transform(X_train_balanced[list_ncorr_features])
X_train_s = scaler.transform(X_train[list_ncorr_features])
X_valid_s = scaler.transform(X_valid[list_ncorr_features])

# time: 10s

In [729]:
# Зададим список solvers
solvers_list = ['lbfgs', 'liblinear', 'newton-cg', 'newton-cholesky', 'sag', 'saga']

# сформируем список для заполнения
solvers_data = []

# установим ограничение на время обучения модели в 180 секунд (3 минут)
time_out = 180

for solver in solvers_list:
        # для того чтобы следить за выполнением цикла введем индикатор
        print('current solver: ', solver)

         # сформируем список для заполнения данными текушего solver
        current_solver_data = [solver]
        
        try:
                # для модуля func_time_out упакуем обучение модели в функцию try_func
                def try_func():
                        logistic_regression = linear_model.LogisticRegression(solver= solver,
                                                                  random_state=42, 
                                                                  max_iter=10000)
                        return logistic_regression.fit(X_train_s_balanced,y_train_balanced)
                    
                # фиксируем время начала
                start_time = time.time()
                
                # запускаем обучение модели с ограничением по времени
                logistic_regression = func_timeout.func_timeout(time_out, try_func)
                
                # фиксируем время окончания обучения
                end_time = time.time()
                
                # запишем время обучения модели
                current_solver_data.append(round(end_time-start_time))

                # Делаем предсказание для обучающей и валидационной выборки
                y_valid_lr_pred = logistic_regression.predict(X_valid_s)
                
                # для метрик ROC AUC делаем предсказание модели для обучающей и валидационной выборки  
                # в виде вероятности принадлежности к классу 1 
                y_train_lr_pred_proba = logistic_regression.predict_proba(X_train_s)[:,1]
                y_valid_lr_pred_proba = logistic_regression.predict_proba(X_valid_s)[:,1]

                #Считаем метрики ROC AUC yна обуающем и валидационном наборе и добавляем их в спискок
                current_solver_data.append(round(metrics.roc_auc_score(y_train, y_train_lr_pred_proba),3))
                current_solver_data.append(round(metrics.roc_auc_score(y_valid, y_valid_lr_pred_proba),3))

                #Считаем метрики для класса 0 на валидационном наборе и добавляем их в список
                current_solver_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))
                current_solver_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))


                #Считаем метрики для класса 1 на валидационном набопе и добавляем их в список
                current_solver_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))
                current_solver_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))

                # запишем данные полученные на одной итерации
                solvers_data.append(current_solver_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                solvers_pd =pd.DataFrame(
                        columns=['solver','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = solvers_data)
                # сохраняем dataframe
                solvers_pd.to_csv('data_recovery/solvers_pd.csv',index=False)
               
                # очистим output от прошедшей итерации
                clear_output()

        except func_timeout.FunctionTimedOut:
                # если время обучения привышает лимит
                # запишем в current_solver_data соотвествующую данные
                current_solver_data = [solver,'>3m',0,0,0,0,0,0]
                # добавляем полученные данные в список solvers_data
                solvers_data.append(current_solver_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                solvers_pd =pd.DataFrame(
                        columns=['solver','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = solvers_data)
                # сохраняем dataframe
                solvers_pd.to_csv('data_recovery/solvers_pd.csv',index=False)
                
                # очистим output от прошедшей итерации
                clear_output()
                # переходим к следующему solver
                pass
# очистим output
clear_output()

# сформируем данные соотвествующие лучщему ROC AUC на валидацинном наборе
best_roc_valid_data = solvers_pd[solvers_pd['roc_valid']==solvers_pd['roc_valid'].max()]

# выведем лучший результат на валидационном наборе
print('result:')
print('best solver on valid:',best_roc_valid_data.iloc[0]['solver'])
print('ROC AUC on train:', best_roc_valid_data.iloc[0]['roc_train'])
print('ROC AUC on valid:', best_roc_valid_data.iloc[0]['roc_valid'])
print('Time fit for best solver:', best_roc_valid_data.iloc[0]['time_fit'],' seconds')

# выведем полученный dataframe
solvers_pd

# time: 2m 35s

result:
best solver on valid: lbfgs
ROC AUC on train: 0.613
ROC AUC on valid: 0.617
Time fit for best solver: 0  seconds


solver  time_fit  roc_train  roc_valid  recall_0  precision_0  \
0            lbfgs         0      0.613      0.617      0.56        0.975   
1        liblinear         0      0.613      0.617      0.56        0.975   
2        newton-cg         0      0.613      0.617      0.56        0.975   
3  newton-cholesky         0      0.613      0.617      0.56        0.975   
4              sag         4      0.613      0.617      0.56        0.975   
5             saga         5      0.613      0.617      0.56        0.975   

   recall_1  precision_1  
0      0.61        0.048  
1      0.61        0.048  
2      0.61        0.048  
3      0.61        0.048  
4      0.61        0.048  
5      0.61        0.048

##### <span style="color:MediumSlateBlue">Подбор гиперпараметров модели</span>

In [1688]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'late'
count_features = dict_spaces[feature_space]

# для работы функции corr_transform_to_force
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()

# для выбора sceler преобразвания нам понадобится словарь
dict_scalers ={
    'MinMaxScaler': MinMaxScaler(),
    'RobustScaler':RobustScaler(),
    'StandardScaler':StandardScaler()}

# настроим оптимизацию гипер параметров
def optuna_lg(trial):
  # задаем пространства поиска гиперпараметров
  solver = trial.suggest_categorical("solver", ['lbfgs', 'liblinear', 'newton-cg', 'newton-cholesky'])
  C = trial.suggest_float('C',0.01,1)
  class_0_weight = trial.suggest_float('class_0_weight',0.2,0.6)
  class_1_weight = trial.suggest_float('class_1_weight',0.2,0.6)
  threshold = trial.suggest_float('threshold',0.6,1)
  class_1_percent = trial.suggest_float('class_1_percent',0.01,0.3)
  scaler = trial.suggest_categorical("scaler", ['MinMaxScaler','RobustScaler','StandardScaler'])
  random_state = trial.suggest_int('random_state', 1, 1000000)


  # создаем модель
  optuna_log_reg = linear_model.LogisticRegression(
      solver=solver,
      C=C,
      class_weight={0:class_0_weight,1:class_1_weight},
      random_state=random_state,
      max_iter=10000)

  # с помощью функции corr_transform_to_force получим
  # список не коррелируемых признаков
  list_ncorr_features = corr_transform_to_force(corr_matrix,threshold=threshold)[1]

  # обьявим scaler
  scaler = dict_scalers[scaler]

  # сформируем данные для анализа сбалансированности обучающих данных
  X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
  y_train_pd = pd.read_csv('target/target_train.csv')

  # поготовим данные y_train_pd к работе с функцией class_1_percent_samples
  y_train_pd.set_index('id',drop=False,inplace=True)

  # подготовим данные для обучения модели
  # с помощью функции class_1_percent_samples зададим долю 
  # класса 1
  list_c1_percent_id = class_1_percent_samples(y_train_pd,class_1_percent,random_state=random_state)[:1000000]

  # подготовим данные для обучения
  X_train_s_balanced = scaler.fit_transform(X_train_pd.loc[list_c1_percent_id])
  y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

  # освободим память от "тяжелых" и ненужных файлов
  del X_train_pd, y_train_pd
  gc.collect()

  # я не воспользовался параметром timeout метода optimize потому, что  
  # optimize отставливает поиск параметров, если время обучения 
  # превышает timeout. Мне нужно чтобы поиск параметров продолжился.
  try:
    # для модуля func_time_out упакуем обучение модели в функцию try_func
    def try_func():
            return optuna_log_reg.fit(X_train_s_balanced, y_train_balanced)
    # обучаем модель с ограничением по времени 10 минут (600 секунд)
    optuna_log_reg = func_timeout.func_timeout(600, try_func)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train_s_balanced, y_train_balanced
    gc.collect()

    # загружаем тестовые наборы
    # сформируем данные для анализа сбалансированности обучающих данных
    X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
    X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()[list_ncorr_features]
    y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
    y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

    # подготовим данные для проверки модели
    X_train_s = scaler.transform(X_train)
    X_valid_s = scaler.transform(X_valid)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train, X_valid
    gc.collect()

    # делаем предсказание на обучающем и валидационном наборе и считаем метрики
    roc_train = metrics.roc_auc_score(y_train, optuna_log_reg.predict_proba(X_train_s)[:,1])
    roc_valid = metrics.roc_auc_score(y_valid, optuna_log_reg.predict_proba(X_valid_s)[:,1])
    f1_score = metrics.f1_score(y_valid, optuna_log_reg.predict(X_valid_s))
    recall_1 = metrics.recall_score(y_valid, optuna_log_reg.predict(X_valid_s),average=None,zero_division=0)[1]
    precision_1 = metrics.precision_score(y_valid, optuna_log_reg.predict(X_valid_s),average=None,zero_division=0)[1]

    # удаляем крупные файлы чтобы высвободить память 
    del X_train_s, X_valid_s, y_train, y_valid
    gc.collect()

  except func_timeout.FunctionTimedOut:
    # удаляем крупные файлы чтобы высвободить память 
    del X_train_s_balanced, y_train_balanced
    gc.collect()
    
    # фиксируем пустые значения метрик
    roc_train = 0
    roc_valid = 0
    f1_score = 0
    recall_1 = 0
    precision_1 = 0
    pass

  return roc_train, roc_valid, f1_score, recall_1, precision_1

In [1689]:
# cоздаем объект исследования
# чтобы модель не переобучалась минимизируем roc_train 
# и максимизируем roc_valid
optuna_study_lg = optuna.create_study(study_name='LogisticRegression_'+feature_space+'_stat', 
                               directions=['maximize','maximize','maximize','maximize','maximize'], 
                               sampler=optuna.samplers.TPESampler(),
                               pruner='Hyperband',
                               storage='sqlite:///optuna_studies.db',
                               load_if_exists=True)
# optuna.delete_study(study_name='LogisticRegression_'+feature_space+'_stat', storage='sqlite:///optuna_studies.db')

[I 2025-04-19 14:42:21,540] Using an existing study with name 'LogisticRegression_late_stat' instead of creating a new one.


In [732]:
# ищем лучшую комбинацию гиперпараметров n_trials раз
optuna_study_lg.optimize(optuna_lg, n_trials=300)

[I 2025-04-17 22:25:46,031] Trial 0 finished with values: [0.6146870343339073, 0.617874310061057, 0.0, 0.0, 0.0] and parameters: {'solver': 'lbfgs', 'C': 0.16944280278684193, 'class_0_weight': 0.4773427386729539, 'class_1_weight': 0.31395889426651136, 'threshold': 0.9277499600591596, 'class_1_percent': 0.0687079344087839, 'scaler': 'StandardScaler', 'random_state': 560041}.
[I 2025-04-17 22:25:51,240] Trial 1 finished with values: [0.6131106858238666, 0.6168359296611097, 0.0007952286282306163, 0.00039952057530962844, 0.08333333333333333] and parameters: {'solver': 'liblinear', 'C': 0.6197279586445118, 'class_0_weight': 0.4639055578583755, 'class_1_weight': 0.27619796790416584, 'threshold': 0.6306309727372926, 'class_1_percent': 0.17066614973066666, 'scaler': 'StandardScaler', 'random_state': 130796}.
[I 2025-04-17 22:25:57,022] Trial 2 finished with values: [0.6146343163264955, 0.6179921258293559, 0.09760616254692604, 0.3999200958849381, 0.05558640604175922] and parameters: {'solver': 

In [1690]:
# из полученного результат соврмируем Data Frame
optuna_study_lg_pd = optuna_study_lg.trials_dataframe().dropna()
# переименуем столбы
optuna_study_lg_pd.rename(columns={
    'values_0': 'roc_train',
    'values_1': 'roc_valid',
    'values_2': 'f1_score',
    'values_3': 'recall_1',
    'values_4': 'precision_1'
},inplace=True)
# Выделим время потраченное на обучение модели
optuna_study_lg_pd.tail()

number  roc_train  roc_valid  f1_score  recall_1  precision_1  \
295     295   0.614241   0.617623  0.089968  0.600879     0.048624   
296     296   0.614412   0.617169  0.097502  0.385138     0.055816   
297     297   0.614723   0.618043  0.103605  0.341590     0.061063   
298     298   0.614354   0.617261  0.089510  0.593688     0.048404   
299     299   0.614305   0.617814  0.070576  0.053136     0.105055   

                datetime_start          datetime_complete  \
295 2025-04-17 23:02:09.567072 2025-04-17 23:02:19.462941   
296 2025-04-17 23:02:19.468270 2025-04-17 23:02:29.740757   
297 2025-04-17 23:02:29.745976 2025-04-17 23:02:39.523721   
298 2025-04-17 23:02:39.529418 2025-04-17 23:02:49.921132   
299 2025-04-17 23:02:49.927084 2025-04-17 23:03:00.231516   

                  duration  params_C  params_class_0_weight  \
295 0 days 00:00:09.895869  0.373571               0.249347   
296 0 days 00:00:10.272487  0.404006               0.280041   
297 0 days 00:00:09.777745  0.348261               0.288518   
298 0 days 00:00:10.391714  0.381832               0.241629   
299 0 days 00:00:10.304432  0.387358               0.260046   

     params_class_1_percent  params_class_1_weight  params_random_state  \
295                0.294921               0.589644               625732   
296                0.299735               0.597663               623482   
297                0.299872               0.574818               808566   
298                0.290305               0.583397               654707   
299                0.288557               0.234822               600060   

      params_scaler params_solver  params_threshold     state  
295    MinMaxScaler         lbfgs          0.816192  COMPLETE  
296    RobustScaler         lbfgs          0.795199  COMPLETE  
297  StandardScaler         lbfgs          0.832323  COMPLETE  
298    RobustScaler         lbfgs          0.816402  COMPLETE  
299    RobustScaler         lbfgs          0.826689  COMPLETE

In [1691]:
# покаждем статистику обучения
print('Максимальное значение метрики ROC AUC на валидационном наборе:',round(optuna_study_lg_pd['roc_valid'].max(),3))
print('Среднее значение метрики ROC AUC на валидационном наборе:',round(optuna_study_lg_pd['roc_valid'].mean(),3))
print('Максимальное значение метрики f1_score на валидационном наборе:',round(optuna_study_lg_pd['f1_score'].max(),3))
print('Среднее значение метрики f1_score на валидационном наборе:',round(optuna_study_lg_pd['f1_score'].mean(),3))
print('Максимальное значение метрики recall_1 на валидационном наборе:',round(optuna_study_lg_pd['recall_1'].max(),3))
print('Среднее значение метрики recall_1 на валидационном наборе:',round(optuna_study_lg_pd['recall_1'].mean(),3))
print('Максимальное значение метрики precision_1 на валидационном наборе:',round(optuna_study_lg_pd['precision_1'].max(),3))
print('Среднее значение метрики precision_1 на валидационном наборе:',round(optuna_study_lg_pd['precision_1'].mean(),3))

Максимальное значение метрики ROC AUC на валидационном наборе: 0.621
Среднее значение метрики ROC AUC на валидационном наборе: 0.618
Максимальное значение метрики f1_score на валидационном наборе: 0.112
Среднее значение метрики f1_score на валидационном наборе: 0.086
Максимальное значение метрики recall_1 на валидационном наборе: 0.745
Среднее значение метрики recall_1 на валидационном наборе: 0.21
Максимальное значение метрики precision_1 на валидационном наборе: 1.0
Среднее значение метрики precision_1 на валидационном наборе: 0.083


In [1694]:
# Визуализируем метрики полученные при optuna оптимизации
fig = px.scatter(
    data_frame=optuna_study_lg_pd[(optuna_study_lg_pd['roc_valid']>0.9999*optuna_study_lg_pd['roc_valid'].max())],
    x='number', #ось абсцисс
    y=['roc_train','roc_valid','recall_1','precision_1'], #ось ординат
)
fig.update_layout(
    title ={
        'text':'Зависимость качества модели от trials optuna', # Имя рабочей плоскости
        'font':{'size':35,'family':"Times New Roman"}, # размер и стиль написания имени рабочей плоскости
        'x':0.5, # Смешение имени по оси "x" на половину рабочей плоскости
        },
    height =800,# Высота рабочей плоскости
    width = 1350, # Ширина рабочей плоскости
    bargap=0.2, # Добавил расстояния между столбами гистограммы
    xaxis_title='trials optuna',
    yaxis_title='Величина метрики')
fig.update_xaxes(showspikes=True)
fig.update_yaxes(showspikes=True)

fig.show()

<span style="color:Blue">

Вывод:  

Их всех выбираем точку $number =108$.   
В этой точке самые оптимальные значения $recall$ и $precision$.  
Посмотрим каким значениям гиперпараметров соотвествует выбранная точка.

In [1695]:
# определим номер лучшге варианта
best_optuna_number = 108

# сформируем словарь лучших гипирпарметров RandomForestClassifier
best_param_lr = {
    'solver' : optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_solver'].iloc[0],
    'C' : round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_C'].iloc[0],3),
    'class_weight' : {0:round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_class_0_weight'].iloc[0],3),
                      1:round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_class_1_weight'].iloc[0],3)},
    }

# создадим перменные
best_threshold = optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_threshold'].iloc[0]
best_scaler = optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_scaler'].iloc[0]
best_class_1_percent = optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_class_1_percent'].iloc[0]
best_random_state = optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_random_state'].iloc[0]

# Выведем принятые наилучшие праметры
print('best solver:',best_param_lr['solver'])
print('best C:',best_param_lr['C'])
print('best class 0 weight:',best_param_lr['class_weight'][0])
print('best class 1 weight:',best_param_lr['class_weight'][1])

print('best class 1 percent:',round(best_class_1_percent,3))
print('best scaler:',best_scaler)
print('best threshold:',round(best_threshold,3))
print('best best random state:',best_random_state)
print('time for best train:',round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['duration'].iloc[0].seconds/60),'minutes')

print()
print('ROC AUC на обучающем наборе:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['roc_train'].iloc[0],3))
print('ROC AUC на валидационном наборе:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['roc_valid'].iloc[0],3))
print('precision класса 1:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['precision_1'].iloc[0],3))
print('recall класса 1:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['recall_1'].iloc[0],3))


best solver: lbfgs
best C: 0.467
best class 0 weight: 0.452
best class 1 weight: 0.508
best class 1 percent: 0.25
best scaler: RobustScaler
best threshold: 0.748
best best random state: 783797
time for best train: 0 minutes

ROC AUC на обучающем наборе: 0.617
ROC AUC на валидационном наборе: 0.621
precision класса 1: 0.108
recall класса 1: 0.058


##### <span style="color:MediumSlateBlue">Обучение модели с лучшими параметрами</span>

In [1696]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'late'
count_features = dict_spaces[feature_space]

# для работы функции corr_transform_to_force
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()

# подготовим данные
# для выбора sceler преобразвания нам понадобится словарь
dict_scalers ={
    'MinMaxScaler': MinMaxScaler(),
    'RobustScaler':RobustScaler(),
    'StandardScaler':StandardScaler(),
}

# с помощью функции corr_transform_to_force получим
# список не коррелируемых признаков
list_ncorr_features = corr_transform_to_force(corr_matrix,threshold=best_threshold)[1]

# обьявим scaler
scaler = dict_scalers[best_scaler]

# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
y_train_pd = pd.read_csv('target/target_train.csv')

# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)

# подготовим данные для обучения модели
# с помощью функции class_1_percent_samples зададим долю 
# класса 1
list_c1_percent_id = class_1_percent_samples(y_train_pd,best_class_1_percent,random_state=best_random_state)[:1000000]

# подготовим данные для обучения
X_train_s_balanced = scaler.fit_transform(X_train_pd.loc[list_c1_percent_id])
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

# освободим память от "тяжелых" и ненужных файлов
del X_train_pd, y_train_pd
gc.collect()


# обучаем модель LogisticRegression с наилучшеми параметрами
logistic_regression = linear_model.LogisticRegression(
        **best_param_lr,
        random_state=42,
        max_iter=10000)
logistic_regression.fit(X_train_s_balanced, y_train_balanced)

# удаляем крупные файлы чтобы высвободить память 
del X_train_s_balanced, y_train_balanced
gc.collect()

# загружаем тестовые наборы
# сформируем данные для анализа сбалансированности обучающих данных
X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()[list_ncorr_features]
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

# подготовим данные для проверки модели
X_train_s = scaler.transform(X_train)
X_valid_s = scaler.transform(X_valid)

# удаляем крупные файлы чтобы высвободить память 
del X_train, X_valid
gc.collect()

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_lr_pred_proba = logistic_regression.predict_proba(X_train_s)[:,1]
y_valid_lr_pred_proba = logistic_regression.predict_proba(X_valid_s)[:,1]

# Делаем предсказание для валидационной выборки
y_valid_lr_pred = logistic_regression.predict(X_valid_s)

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_lr_pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_lr_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_lr_pred,zero_division=0))

# time: 2m 30s

ROC AUC на обучающем наборе 0.617
ROC AUC на валидационном наборе 0.621
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.97      0.98      0.97     68747
           1       0.11      0.06      0.07      2503

    accuracy                           0.95     71250
   macro avg       0.54      0.52      0.52     71250
weighted avg       0.94      0.95      0.94     71250



#### <span style="color:MediumBlue">Построение модели Random Forest Classifier</span>

##### <span style="color:MediumSlateBlue">Формирование данных для обучения</span>

Анализ исходных данных, в частности target, показал что представленные данные   
имееют перекос: 96% клиентов у которых не случился дефолт (flag = 0),    
против 4 % - для которых произошел дефолт (flag = 1).  
С помощью функции class_1_percent_samples, сформируем сбаланисрованную выборку  
для обучения моделей.
За основу сбалансировных данных возьмем данные клиентов с дефолтом  
и к ним будем добирать необходимое количество клиентов до сбалансированности. 


Функция class_1_percent_samples принемает две переменные:
- target_data - массив с id и целевой переменной
- class_1_percent - процент класса 1 в результирующем массиве

In [751]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'late'
count_features = dict_spaces[feature_space]

In [752]:
# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

In [753]:
# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)
y_train_pd.head(4)

id  flag
id                    
1825800  1825800     0
2166483  2166483     0
2534345  2534345     0
1803283  1803283     0

In [754]:
# взглянем на сблансиорованность данных в y_train
y_train_pd['flag'].value_counts(normalize=True)

flag
0    0.964242
1    0.035758
Name: proportion, dtype: float64

In [755]:
# сбалансируем данные в y_train_pd
list_c1_percent_id = class_1_percent_samples(y_train_pd,0.5)
# list_c1_percent_features - список 'id' из y_train_pd соотвествующих  
# заданному проценту класса 1
len(list_c1_percent_id)

45860

In [756]:
# проверим сбалансированность полученного y_train
y_train_pd.loc[list_c1_percent_id]['flag'].value_counts(normalize=True)

flag
1    0.5
0    0.5
Name: proportion, dtype: float64

В отличие от данных в *transform_data_torow*, где модели показываеются последние N  
операций клиента, в данные в *transform_data_stat* сфомированы из различных статистических   
характеристик ряда определяющего клиентскую историю в банке. 

Соотвественно, если в данных *transform_data_torow* была сильная корреляция между признаками,  
то я не смог бы ее убрать, иначе потярется смысл "показать последовательный ряд в историии клиента".  
Признаки в *transform_data_stat* не имеют такой особенности. Поэтому, необходимо проанализировать  
данные в *transform_data_stat* и, в случае сильной коррреляции признаков, устранить ее.

In [757]:
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()
corr_matrix.shape

(205, 205)

In [758]:
# с помощью функции corr_transrom_to_power получим
# силу корреляции матрицы и список не коррелируемых признаков

# для начального анализа зададим порог силы корреляции, при котором признаки 
# будут отнесены к "сильно скоррелированными" равным 0.6
ncorr_matrix,list_ncorr_features,corr_power =corr_transform_to_force(corr_matrix,threshold=0.6)

# Выведем результаты преобразования
print('Исходное количество признаков: ', corr_matrix.shape[0])
print('Количество не коррелируемых признаков: ', len(list_ncorr_features))
# сила корреляции признаков
print('Отношение коррелируемых исходному количеству признаков (сила корреляции): ',corr_power)

Исходное количество признаков:  205
Количество не коррелируемых признаков:  67
Отношение коррелируемых исходному количеству признаков (сила корреляции):  0.673


In [759]:
# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']
# сформируем данные для проверики модели
# сформируем данные для анализа сбалансированности обучающих данных
X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()
y_train = pd.read_csv('target/target_train.csv')['flag']
X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()
y_valid = pd.read_csv('target/target_valid.csv')['flag']

In [760]:
# посмотрим на структуру данных в X_train_balanced
X_train_balanced.head(4)

f1   f2   f3   f4   f5   f6   f7   f8   f9  f10  ...   f196  f197  \
id                                                          ...                
2335465  17.0  0.0  6.0  6.0  6.0  6.0  6.0  0.0  0.0  6.0  ...  0.000   2.0   
390270    6.0  0.0  6.0  6.0  6.0  6.0  6.0  0.0  0.0  6.0  ...  0.000   2.0   
2494034  14.0  0.0  6.0  6.0  6.0  6.0  6.0  0.0  0.0  6.0  ...  0.000   2.0   
2018674  15.0  0.0  6.0  6.0  6.0  6.0  6.0  0.0  0.0  6.0  ...  0.249   2.0   

         f198  f199  f200  f201  f202  f203   f204  f205  
id                                                        
2335465   2.0   2.0   2.0   2.0   2.0  1.00  0.000   2.0  
390270    2.0   2.0   2.0   2.0   2.0  1.00  0.000   2.0  
2494034   2.0   2.0   2.0   2.0   2.0  1.00  0.000   2.0  
2018674   2.0   2.0   2.0   3.0   2.0  0.93  0.067   2.5  

[4 rows x 205 columns]

In [761]:
# посмотрим на структуру данных в y_train_balanced
y_train_balanced.head(4)

id
2335465    1
390270     1
2494034    1
2018674    1
Name: flag, dtype: int64

In [762]:
# проверим что выборки действительно совпадают по id
X_train_balanced.index.to_list() == y_train_balanced.index.to_list()

True

##### <span style="color:MediumSlateBlue">Baseline обучение модели RandomForestClassifier</span>

In [763]:
# обучаем модель логистической регрессии
# чтобы модель пыталась найти связь во всех признаках
random_forest = RandomForestClassifier(random_state=42, n_jobs=-1)
random_forest.fit(X_train_balanced[list_ncorr_features],y_train_balanced)

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_rf__pred_proba = random_forest.predict_proba(X_train[list_ncorr_features])[:,1]
y_valid_rf_pred_proba = random_forest.predict_proba(X_valid[list_ncorr_features])[:,1]

# Делаем предсказание для валидационной выборки
y_valid_rf_pred = random_forest.predict(X_valid[list_ncorr_features])

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_rf__pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_rf_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_rf_pred))

# time: 17s

ROC AUC на обучающем наборе 0.717
ROC AUC на валидационном наборе 0.584
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.97      0.64      0.77     68747
           1       0.05      0.50      0.09      2503

    accuracy                           0.63     71250
   macro avg       0.51      0.57      0.43     71250
weighted avg       0.94      0.63      0.75     71250



##### <span style="color:MediumSlateBlue">Подбор гиперпараметров модели</span>

In [1697]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'late'
count_features = dict_spaces[feature_space]

# для работы функции corr_transform_to_force
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()

# настроим оптимизацию гипер параметров
def optuna_rf(trial):
  # задаем пространства поиска гиперпараметров
  # задаем пространства поиска гиперпараметров
  n_estimators = trial.suggest_int('n_estimators', 40, 100,step = 5)
  criterion = trial.suggest_categorical('criterion',['gini', 'entropy', 'log_loss'])
  max_depth = trial.suggest_int('max_depth', 10, 30,step = 1)
  min_samples_split = trial.suggest_int('min_samples_split', 5, 15,step = 1)
  min_samples_leaf = trial.suggest_int('min_samples_leaf', 5, 15,step = 1)
  max_features = trial.suggest_float('max_features',0.4,0.8)
  max_samples = trial.suggest_float('max_samples',0.4,0.8)
  class_0_weight = trial.suggest_float('class_0_weight',0.1,1)
  class_1_weight = trial.suggest_float('class_1_weight',0.1,1)
  threshold = trial.suggest_float('threshold',0.4,0.8)
  class_1_percent = trial.suggest_float('class_1_percent',0.01,0.5)
  random_state = trial.suggest_int('random_state', 1, 1000000)


  # создаем модель
  optuna_random_forest = RandomForestClassifier(
      n_estimators = n_estimators, 
      criterion = criterion,
      max_depth = max_depth,
      min_samples_split = min_samples_split,  
      min_samples_leaf = min_samples_leaf,
      max_features=max_features,
      max_samples=max_samples,
      class_weight={0:class_0_weight,1:class_1_weight},
      n_jobs=-1,
      random_state=42)

  # с помощью функции corr_transform_to_force получим
  # список не коррелируемых признаков
  list_ncorr_features = corr_transform_to_force(corr_matrix,threshold=threshold)[1]

  # сформируем данные для анализа сбалансированности обучающих данных
  X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
  y_train_pd = pd.read_csv('target/target_train.csv')

  # поготовим данные y_train_pd к работе с функцией class_1_percent_samples
  y_train_pd.set_index('id',drop=False,inplace=True)

  # подготовим данные для обучения модели
  # с помощью функции class_1_percent_samples зададим долю 
  # класса 1
  list_c1_percent_id = class_1_percent_samples(y_train_pd,class_1_percent,random_state=random_state)[:1000000]

  # подготовим данные для обучения
  X_train_balanced = X_train_pd.loc[list_c1_percent_id]
  y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']

  # освободим память от "тяжелых" и ненужных файлов
  del X_train_pd, y_train_pd
  gc.collect()

  # я не воспользовался параметром timeout метода optimize потому, что  
  # optimize отставливает поиск параметров, если время обучения 
  # превышает timeout. Мне нужно чтобы поиск параметров продолжился.
  try:
    # для модуля func_time_out упакуем обучение модели в функцию try_func
    def try_func():
            return optuna_random_forest.fit(X_train_balanced, y_train_balanced)
    # обучаем модель с ограничением по времени 10 минут (600 секунд)
    optuna_random_forest = func_timeout.func_timeout(600, try_func)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train_balanced, y_train_balanced
    gc.collect()

    # загружаем тестовые наборы
    # сформируем данные для анализа сбалансированности обучающих данных
    X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
    X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()[list_ncorr_features]
    y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
    y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()
    
    # делаем предсказание на обучающем и валидационном наборе
    #Считаем метрики для класса 1 добавляем их в список
    roc_train = metrics.roc_auc_score(y_train, optuna_random_forest.predict_proba(X_train)[:,1])
    roc_valid = metrics.roc_auc_score(y_valid, optuna_random_forest.predict_proba(X_valid)[:,1])
    f1_score = metrics.f1_score(y_valid, optuna_random_forest.predict(X_valid))
    recall_1 = metrics.recall_score(y_valid, optuna_random_forest.predict(X_valid),average=None,zero_division=0)[1]
    precision_1 = metrics.precision_score(y_valid, optuna_random_forest.predict(X_valid),average=None,zero_division=0)[1]

    # удаляем крупные файлы чтобы высвободить память 
    del X_train, X_valid, y_train, y_valid
    gc.collect()

  except func_timeout.FunctionTimedOut:
    # удаляем крупные файлы чтобы высвободить память 
    del X_train_balanced, y_train_balanced
    gc.collect()
    
    # фиксируем пустые значения метрик
    roc_train = 0
    roc_valid = 0
    f1_score = 0
    recall_1 = 0
    precision_1 = 0
    pass

  return roc_train, roc_valid, f1_score, recall_1, precision_1

In [1698]:
# cоздаем объект исследования
optuna_study_rf = optuna.create_study(study_name= 'RandomForestClassifier_'+feature_space+'_stat', 
                               directions=['maximize','maximize','maximize','maximize','maximize'], 
                               sampler=optuna.samplers.TPESampler(),
                               pruner='Hyperband',
                               storage='sqlite:///optuna_studies.db',
                               load_if_exists=True)
# на случай удаления 
# optuna.delete_study(study_name='RandomForestClassifier_'+feature_space+'_stat', storage='sqlite:///optuna_studies.db')

[I 2025-04-19 14:45:02,438] Using an existing study with name 'RandomForestClassifier_late_stat' instead of creating a new one.


In [766]:
# ищем лучшую комбинацию гиперпараметров n_trials раз
optuna_study_rf.optimize(optuna_rf, n_trials=300)

[I 2025-04-17 23:03:34,313] Trial 0 finished with values: [0.6946008636601059, 0.6084558044216637, 0.09933549983023718, 0.4091090691170595, 0.0565308601082036] and parameters: {'n_estimators': 55, 'criterion': 'log_loss', 'max_depth': 30, 'min_samples_split': 5, 'min_samples_leaf': 15, 'max_features': 0.4211799055504628, 'max_samples': 0.771789313539867, 'class_0_weight': 0.1313706240099441, 'class_1_weight': 0.5258551068516525, 'threshold': 0.7104441628439593, 'class_1_percent': 0.18880599737396134, 'random_state': 528699}.
[I 2025-04-17 23:03:38,788] Trial 1 finished with values: [0.6571901990083621, 0.6177286399555875, 0.10304789550072568, 0.2836596084698362, 0.06296000709408531] and parameters: {'n_estimators': 45, 'criterion': 'log_loss', 'max_depth': 16, 'min_samples_split': 14, 'min_samples_leaf': 5, 'max_features': 0.758278053239746, 'max_samples': 0.5342417178134283, 'class_0_weight': 0.5642024108130727, 'class_1_weight': 0.5235607108030293, 'threshold': 0.4964379612364589, 'c

In [1699]:
# из полученного результат соврмируем Data Frame
optuna_study_rf_pd = optuna_study_rf.trials_dataframe().dropna()
# переименуем столбы
optuna_study_rf_pd.rename(columns={
    'values_0': 'roc_train',
    'values_1': 'roc_valid',
    'values_2': 'f1_score',
    'values_3': 'recall_1',
    'values_4': 'precision_1'
},inplace=True)
optuna_study_rf_pd.tail()

number  roc_train  roc_valid  f1_score  recall_1  precision_1  \
295     295   0.733524   0.597806  0.097129  0.155414     0.070637   
296     296   0.682317   0.615938  0.102751  0.399920     0.058948   
297     297   0.693024   0.605535  0.079037  0.755094     0.041701   
298     298   0.688369   0.617962  0.088608  0.081103     0.097643   
299     299   0.678038   0.617969  0.103047  0.157411     0.076594   

                datetime_start          datetime_complete  \
295 2025-04-17 23:45:18.994161 2025-04-17 23:45:32.982698   
296 2025-04-17 23:45:32.988670 2025-04-17 23:45:44.882945   
297 2025-04-17 23:45:44.888781 2025-04-17 23:45:56.336964   
298 2025-04-17 23:45:56.343040 2025-04-17 23:46:12.981522   
299 2025-04-17 23:46:12.987310 2025-04-17 23:46:24.775920   

                  duration  params_class_0_weight  ...  params_criterion  \
295 0 days 00:00:13.988537               0.160895  ...           entropy   
296 0 days 00:00:11.894275               0.188717  ...              gini   
297 0 days 00:00:11.448183               0.153370  ...          log_loss   
298 0 days 00:00:16.638482               0.147333  ...              gini   
299 0 days 00:00:11.788610               0.188937  ...              gini   

     params_max_depth params_max_features  params_max_samples  \
295                27            0.500202            0.722383   
296                14            0.772754            0.700352   
297                19            0.772479            0.731821   
298                14            0.761766            0.730116   
299                13            0.591859            0.738351   

     params_min_samples_leaf  params_min_samples_split  params_n_estimators  \
295                        9                         9                   95   
296                        8                         8                  100   
297                       13                         8                   60   
298                       13                         8                  100   
299                        8                         8                   60   

     params_random_state  params_threshold     state  
295                95996          0.769399  COMPLETE  
296               507280          0.703775  COMPLETE  
297               508713          0.699599  COMPLETE  
298               349605          0.704010  COMPLETE  
299               539952          0.704556  COMPLETE  

[5 rows x 22 columns]

In [1700]:
# покаждем статистику обучения
print('Максимальное значение метрики ROC AUC на валидационном наборе:',round(optuna_study_rf_pd['roc_valid'].max(),3))
print('Среднее значение метрики ROC AUC на валидационном наборе:',round(optuna_study_rf_pd['roc_valid'].mean(),3))
print('Максимальное значение метрики f1_score на валидационном наборе:',round(optuna_study_rf_pd['f1_score'].max(),3))
print('Среднее значение метрики f1_score на валидационном наборе:',round(optuna_study_rf_pd['f1_score'].mean(),3))
print('Максимальное значение метрики recall_1 на валидационном наборе:',round(optuna_study_rf_pd['recall_1'].max(),3))
print('Среднее значение метрики recall_1 на валидационном наборе:',round(optuna_study_rf_pd['recall_1'].mean(),3))
print('Максимальное значение метрики precision_1 на валидационном наборе:',round(optuna_study_rf_pd['precision_1'].max(),3))
print('Среднее значение метрики precision_1 на валидационном наборе:',round(optuna_study_rf_pd['precision_1'].mean(),3))

Максимальное значение метрики ROC AUC на валидационном наборе: 0.627
Среднее значение метрики ROC AUC на валидационном наборе: 0.611
Максимальное значение метрики f1_score на валидационном наборе: 0.11
Среднее значение метрики f1_score на валидационном наборе: 0.078
Максимальное значение метрики recall_1 на валидационном наборе: 1.0
Среднее значение метрики recall_1 на валидационном наборе: 0.347
Максимальное значение метрики precision_1 на валидационном наборе: 0.286
Среднее значение метрики precision_1 на валидационном наборе: 0.074


In [1705]:
# Построим зависимость метрик качества модели от number

fig = px.scatter(
    data_frame=optuna_study_rf_pd[(optuna_study_rf_pd['roc_valid']>=0.999*optuna_study_rf_pd['roc_valid'].max())],
    x='number', #ось абсцисс
    y=['roc_valid','roc_train','precision_1','recall_1'], #ось ординат
)
fig.update_layout(
    title ={
        'text':'Зависимость качества модели от trials optuna', # Имя рабочей плоскости
        'font':{'size':35,'family':"Times New Roman"}, # размер и стиль написания имени рабочей плоскости
        'x':0.5, # Смешение имени по оси "x" на половину рабочей плоскости
        },
    height =800,# Высота рабочей плоскости
    width = 1350, # Ширина рабочей плоскости
    bargap=0.2, # Добавил расстояния между столбами гистограммы
    xaxis_title='trials optuna',
    yaxis_title='Величина параметра')
fig.update_xaxes(showspikes=True)
fig.update_yaxes(showspikes=True)

fig.show()

<span style="color:Blue">

Вывод:  

Их всех выбираем точку $number =186$.   
Не смотря на, то что в этой точке модель подает признаки переобучеености,  
в этой точке оптимальные значения метрик $recall_1$ и $precision_1$, а  
также относительно высокая метрика $ROC AUC$.   
Посмотрим каким значениям гиперпараметров соотвествует выбраннаяточка.

In [1706]:
# определим номер лучшге варианта
best_optuna_number = 186

# сформируем словарь лучших гипирпарметров RandomForestClassifier
best_param_rf = {
    'n_estimators' : int(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_n_estimators'].iloc[0]),
    'criterion': optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_criterion'].iloc[0],
    'max_depth' : int(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_max_depth'].iloc[0]),
    'min_samples_split': int(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_min_samples_split'].iloc[0]),
    'min_samples_leaf' : int(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_min_samples_leaf'].iloc[0]),
    'max_features': optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_max_features'].iloc[0],
    'max_samples' : optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_max_samples'].iloc[0],
    'class_weight' : {0:optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_class_0_weight'].iloc[0],
                      1:optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_class_1_weight'].iloc[0]}
    }

# определим перменные для лучших значений параметров
best_threshold = optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_threshold'].iloc[0]
best_class_1_percent = optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_class_1_percent'].iloc[0]
best_random_state = optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_random_state'].iloc[0]


# Выведем принятые наилучшие праметры
print('best n estimators:',best_param_rf['n_estimators'])
print('best criterion:',best_param_rf['criterion'])
print('best max depth:',best_param_rf['max_depth'])
print('best min samples split:',best_param_rf['min_samples_split'])
print('best min samples leaf:',best_param_rf['min_samples_leaf'])
print('best max features(%):',round(best_param_rf['max_features'],3))
print('best max samples(%):',round(best_param_rf['max_samples'],3))
print('best class 0 weight:',round(best_param_rf['class_weight'][0],3))
print('best class 1 weight:',round(best_param_rf['class_weight'][1],3))

print('best class 1 percent:',round(best_class_1_percent,3))
print('best threshold:',round(best_threshold,3))
print('best random state:', best_random_state)
print('time for best train:',round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['duration'].iloc[0].seconds/60),'minutes')

print()
print('ROC AUC на обучающем наборе:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['roc_train'].iloc[0],3))
print('ROC AUC на валидационном наборе:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['roc_valid'].iloc[0],3))
print('precision класса 1:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['precision_1'].iloc[0],3))
print('recall класса 1:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['recall_1'].iloc[0],3))

best n estimators: 100
best criterion: gini
best max depth: 11
best min samples split: 9
best min samples leaf: 14
best max features(%): 0.418
best max samples(%): 0.732
best class 0 weight: 0.338
best class 1 weight: 0.955
best class 1 percent: 0.074
best threshold: 0.697
best random state: 842262
time for best train: 0 minutes

ROC AUC на обучающем наборе: 0.649
ROC AUC на валидационном наборе: 0.626
precision класса 1: 0.161
recall класса 1: 0.014


##### <span style="color:MediumSlateBlue">Обучение модели с лучшими параметрами</span>

In [1707]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'late'
count_features = dict_spaces[feature_space]

# для работы функции corr_transform_to_force
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()

# с помощью функции corr_transform_to_force получим
# список не коррелируемых признаков
list_ncorr_features = corr_transform_to_force(corr_matrix,threshold=best_threshold)[1]

# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
y_train_pd = pd.read_csv('target/target_train.csv')

# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)

# подготовим данные для обучения модели
# с помощью функции class_1_percent_samples зададим долю 
# класса 1
list_c1_percent_id = class_1_percent_samples(y_train_pd,best_class_1_percent,random_state=best_random_state)[:1000000]

# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']

# освободим память от "тяжелых" и ненужных файлов
del X_train_pd, y_train_pd
gc.collect()


# обучаем модель RandomForestClassifier с наилучшеми параметрами
random_forest = RandomForestClassifier(
        **best_param_rf,
        n_jobs=-1,
        random_state=42)
random_forest.fit(X_train_balanced, y_train_balanced)

# удаляем крупные файлы чтобы высвободить память 
del X_train_balanced, y_train_balanced
gc.collect()

# загружаем тестовые наборы
# сформируем данные для анализа сбалансированности обучающих данных
X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()[list_ncorr_features]
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_rf_pred_proba = random_forest.predict_proba(X_train)[:,1]
y_valid_rf_pred_proba = random_forest.predict_proba(X_valid)[:,1]

# Делаем предсказание для валидационной выборки
y_valid_rf_pred = random_forest.predict(X_valid)

# удаляем крупные файлы чтобы высвободить память 
del X_train, X_valid
gc.collect()

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_rf_pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_rf_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_rf_pred,zero_division=0))

# time: 5m 30s

ROC AUC на обучающем наборе 0.649
ROC AUC на валидационном наборе 0.626
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.97      1.00      0.98     68747
           1       0.16      0.01      0.03      2503

    accuracy                           0.96     71250
   macro avg       0.56      0.51      0.50     71250
weighted avg       0.94      0.96      0.95     71250



#### <span style="color:MediumBlue">Построение модели Gradient Boosting Classifier</span>

##### <span style="color:MediumSlateBlue">Формирование данных для обучения</span>

Анализ исходных данных, в частности target, показал что представленные данные   
имееют перекос: 96% клиентов у которых не случился дефолт (flag = 0),    
против 4 % - для которых произошел дефолт (flag = 1).  
С помощью функции class_1_percent_samples, сформируем сбаланисрованную выборку  
для обучения моделей.
За основу сбалансировных данных возьмем данные клиентов с дефолтом  
и к ним будем добирать необходимое количество клиентов до сбалансированности. 


Функция class_1_percent_samples принемает две переменные:
- target_data - массив с id и целевой переменной
- class_1_percent - процент класса 1 в результирующем массиве

In [784]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'late'
count_features = dict_spaces[feature_space]

In [785]:
# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

In [786]:
# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)
y_train_pd.head(4)

id  flag
id                    
1825800  1825800     0
2166483  2166483     0
2534345  2534345     0
1803283  1803283     0

In [787]:
# взглянем на сблансиорованность данных в y_train
y_train_pd['flag'].value_counts(normalize=True)

flag
0    0.964242
1    0.035758
Name: proportion, dtype: float64

In [788]:
# сбалансируем данные в y_train_pd
list_c1_percent_id = class_1_percent_samples(y_train_pd,0.5)
# list_c1_percent_features - список 'id' из y_train_pd соотвествующих  
# заданному проценту класса 1
len(list_c1_percent_id)

45860

In [789]:
# проверим сбалансированность полученного y_train
y_train_pd.loc[list_c1_percent_id]['flag'].value_counts(normalize=True)

flag
1    0.5
0    0.5
Name: proportion, dtype: float64

В отличие от данных в *transform_data_torow*, где модели показываеются последние N  
операций клиента, в данные в *transform_data_stat* сфомированы из различных статистических   
характеристик ряда определяющего клиентскую историю в банке. 

Соотвественно, если в данных *transform_data_torow* была сильная корреляция между признаками,  
то я не смог бы ее убрать, иначе потярется смысл "показать последовательный ряд в историии клиента".  
Признаки в *transform_data_stat* не имеют такой особенности. Поэтому, необходимо проанализировать  
данные в *transform_data_stat* и, в случае сильной коррреляции признаков, устранить ее.

In [790]:
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()
corr_matrix.shape

(205, 205)

In [791]:
# с помощью функции corr_transrom_to_power получим
# силу корреляции матрицы и список не коррелируемых признаков

# для начального анализа зададим порог силы корреляции, при котором признаки 
# будут отнесены к "сильно скоррелированными" равным 0.6
ncorr_matrix,list_ncorr_features,corr_power =corr_transform_to_force(corr_matrix,threshold=0.6)

# Выведем результаты преобразования
print('Исходное количество признаков: ', corr_matrix.shape[0])
print('Количество не коррелируемых признаков: ', len(list_ncorr_features))
# сила корреляции признаков
print('Отношение коррелируемых исходному количеству признаков (сила корреляции): ',corr_power)

Исходное количество признаков:  205
Количество не коррелируемых признаков:  67
Отношение коррелируемых исходному количеству признаков (сила корреляции):  0.673


In [792]:
# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']
# сформируем данные для проверики модели
# сформируем данные для анализа сбалансированности обучающих данных
X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()
y_train = pd.read_csv('target/target_train.csv')['flag']
X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()
y_valid = pd.read_csv('target/target_valid.csv')['flag']

In [793]:
# посмотрим на структуру данных в X_train_balanced
X_train_balanced.head(4)

f1   f2   f3   f4   f5   f6   f7   f8   f9  f10  ...   f196  f197  \
id                                                          ...                
2335465  17.0  0.0  6.0  6.0  6.0  6.0  6.0  0.0  0.0  6.0  ...  0.000   2.0   
390270    6.0  0.0  6.0  6.0  6.0  6.0  6.0  0.0  0.0  6.0  ...  0.000   2.0   
2494034  14.0  0.0  6.0  6.0  6.0  6.0  6.0  0.0  0.0  6.0  ...  0.000   2.0   
2018674  15.0  0.0  6.0  6.0  6.0  6.0  6.0  0.0  0.0  6.0  ...  0.249   2.0   

         f198  f199  f200  f201  f202  f203   f204  f205  
id                                                        
2335465   2.0   2.0   2.0   2.0   2.0  1.00  0.000   2.0  
390270    2.0   2.0   2.0   2.0   2.0  1.00  0.000   2.0  
2494034   2.0   2.0   2.0   2.0   2.0  1.00  0.000   2.0  
2018674   2.0   2.0   2.0   3.0   2.0  0.93  0.067   2.5  

[4 rows x 205 columns]

In [794]:
# посмотрим на структуру данных в y_train_balanced
y_train_balanced.head(4)

id
2335465    1
390270     1
2494034    1
2018674    1
Name: flag, dtype: int64

In [795]:
# проверим что выборки действительно совпадают по id
X_train_balanced.index.to_list() == y_train_balanced.index.to_list()

True

##### <span style="color:MediumSlateBlue">Baseline обучение модели Hist Gradient Boosting Classifier</span>

In [796]:
# обучаем модель Gradient Boosting Classifier
gradient_boosting = HistGradientBoostingClassifier(random_state=42)
gradient_boosting.fit(X_train_balanced[list_ncorr_features],y_train_balanced)

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_rf__pred_proba = gradient_boosting.predict_proba(X_train[list_ncorr_features])[:,1]
y_valid_rf_pred_proba = gradient_boosting.predict_proba(X_valid[list_ncorr_features])[:,1]

# Делаем предсказание для валидационной выборки
y_valid_rf_pred = gradient_boosting.predict(X_valid[list_ncorr_features])

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_rf__pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_rf_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_rf_pred))

# time: 30s

ROC AUC на обучающем наборе 0.631
ROC AUC на валидационном наборе 0.626
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.97      0.66      0.79     68747
           1       0.05      0.52      0.10      2503

    accuracy                           0.66     71250
   macro avg       0.51      0.59      0.44     71250
weighted avg       0.94      0.66      0.77     71250



##### <span style="color:MediumSlateBlue">Подбор гиперпараметров модели</span>

In [1708]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'late'
count_features = dict_spaces[feature_space]

# для работы функции corr_transform_to_force
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()

# настроим оптимизацию гипер параметров
def optuna_hgbc(trial):
  # задаем пространства поиска гиперпараметров
  learning_rate = trial.suggest_float('learning_rate',0.01,0.1)
  max_iter = trial.suggest_int('max_iter', 150, 250,step = 1)
  max_leaf_nodes = trial.suggest_int('max_leaf_nodes', 2, 60,step = 1)
  max_depth = trial.suggest_int('max_depth', 1, 10,step = 1)
  min_samples_leaf = trial.suggest_int('min_samples_leaf', 1, 60,step = 1)
  max_features = trial.suggest_float('max_features',0.6,1)
  l2_regularization = trial.suggest_float('l2_regularization',0.01,1)
  class_0_weight = trial.suggest_float('class_0_weight',0.01,1)
  class_1_weight = trial.suggest_float('class_1_weight',0.5,1)
  threshold = trial.suggest_float('threshold',0.7,1)
  class_1_percent = trial.suggest_float('class_1_percent',0.01,0.25)
  random_state = trial.suggest_int('random_state', 1, 1000000)

  # создаем модель
  optuna_gradient_boosting = HistGradientBoostingClassifier(
      learning_rate= learning_rate,
      max_iter = max_iter,
      max_leaf_nodes =max_leaf_nodes,
      max_depth = max_depth,
      min_samples_leaf = min_samples_leaf,
      max_features=max_features,
      l2_regularization = l2_regularization,
      class_weight={0:class_0_weight,1:class_1_weight},
      random_state=42)

  # с помощью функции corr_transform_to_force получим
  # список не коррелируемых признаков
  list_ncorr_features = corr_transform_to_force(corr_matrix,threshold=threshold)[1]

  # сформируем данные для анализа сбалансированности обучающих данных
  X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
  y_train_pd = pd.read_csv('target/target_train.csv')

  # поготовим данные y_train_pd к работе с функцией class_1_percent_samples
  y_train_pd.set_index('id',drop=False,inplace=True)

  # подготовим данные для обучения модели
  # с помощью функции class_1_percent_samples зададим долю 
  # класса 1
  list_c1_percent_id = class_1_percent_samples(y_train_pd,class_1_percent,random_state=random_state)[:1000000]

  # подготовим данные для обучения
  X_train_balanced = X_train_pd.loc[list_c1_percent_id]
  y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']

  # освободим память от "тяжелых" и ненужных файлов
  del X_train_pd, y_train_pd
  gc.collect()

  # я не воспользовался параметром timeout метода optimize потому, что  
  # optimize отставливает поиск параметров, если время обучения 
  # превышает timeout. Мне нужно чтобы поиск параметров продолжился.
  try:
    # для модуля func_time_out упакуем обучение модели в функцию try_func
    def try_func():
            return optuna_gradient_boosting.fit(X_train_balanced,y_train_balanced)
    # обучаем модель с ограничением по времени 10 минут (600 секунд)
    optuna_gradient_boosting = func_timeout.func_timeout(600, try_func)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train_balanced, y_train_balanced
    gc.collect()

        # загружаем тестовые наборы
    # сформируем данные для анализа сбалансированности обучающих данных
    X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
    X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()[list_ncorr_features]
    y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
    y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()
    
    # делаем предсказание на обучающем и валидационном наборе и считаем метрики
    roc_train = metrics.roc_auc_score(y_train, optuna_gradient_boosting.predict_proba(X_train)[:,1])
    roc_valid = metrics.roc_auc_score(y_valid, optuna_gradient_boosting.predict_proba(X_valid)[:,1])
    f1_score = metrics.f1_score(y_valid, optuna_gradient_boosting.predict(X_valid))
    recall_1 = metrics.recall_score(y_valid, optuna_gradient_boosting.predict(X_valid),average=None,zero_division=0)[1]
    precision_1 = metrics.precision_score(y_valid, optuna_gradient_boosting.predict(X_valid),average=None,zero_division=0)[1]


    # удаляем крупные файлы чтобы высвободить память 
    del X_train, X_valid, y_train, y_valid
    gc.collect()

  except func_timeout.FunctionTimedOut:
    # удаляем крупные файлы чтобы высвободить память 
    del X_train_balanced, y_train_balanced
    gc.collect()
    
    # фиксируем пустые значения метрик
    roc_train = 0
    roc_valid = 0
    f1_score = 0
    recall_1 = 0
    precision_1 = 0
    pass

  return roc_train, roc_valid, f1_score, recall_1, precision_1

In [1709]:
# cоздаем объект исследования
# чтобы модель не переобучалась минимизируем roc_train 
# и максимизируем roc_valid
optuna_study_hgbc = optuna.create_study(study_name='HistGradientBoostingClassifier_'+feature_space+'_stat', 
                               directions=['maximize','maximize','maximize','maximize','maximize'], 
                               sampler=optuna.samplers.TPESampler(),
                               pruner='Hyperband',
                               storage='sqlite:///optuna_studies.db',
                               load_if_exists=True)

# ну случай удаления обучения
# optuna.delete_study(study_name='HistGradientBoostingClassifier'+feature_space+'_stat', storage='sqlite:///optuna_studies.db')

[I 2025-04-19 14:46:38,897] Using an existing study with name 'HistGradientBoostingClassifier_late_stat' instead of creating a new one.


In [799]:
# ищем лучшую комбинацию гиперпараметров n_trials раз
optuna_study_hgbc.optimize(optuna_hgbc, n_trials=300)

[I 2025-04-17 23:47:07,440] Trial 0 finished with values: [0.6388615650897551, 0.6266851895781124, 0.0, 0.0, 0.0] and parameters: {'learning_rate': 0.037620321460558895, 'max_iter': 160, 'max_leaf_nodes': 56, 'max_depth': 8, 'min_samples_leaf': 22, 'max_features': 0.8279427746712464, 'l2_regularization': 0.5299148687482312, 'class_0_weight': 0.3937075668524809, 'class_1_weight': 0.5883586844435158, 'threshold': 0.8849358538821835, 'class_1_percent': 0.03678809865228624, 'random_state': 393063}.
[I 2025-04-17 23:47:26,544] Trial 1 finished with values: [0.6453853101354163, 0.624489151427236, 0.05304010349288486, 0.03276068717538953, 0.13921901528013583] and parameters: {'learning_rate': 0.06053908395210661, 'max_iter': 169, 'max_leaf_nodes': 50, 'max_depth': 10, 'min_samples_leaf': 44, 'max_features': 0.8457964686168983, 'l2_regularization': 0.6725322621499047, 'class_0_weight': 0.07210701308451013, 'class_1_weight': 0.9209297499614393, 'threshold': 0.8359742729532015, 'class_1_percent'

In [1710]:
# из полученного результат соврмируем Data Frame
optuna_study_hgbc_pd = optuna_study_hgbc.trials_dataframe()
# переименуем столбы
optuna_study_hgbc_pd.rename(columns={
    'values_0': 'roc_train',
    'values_1': 'roc_valid',
    'values_2': 'f1_score',
    'values_3': 'recall_1',
    'values_4': 'precision_1'
},inplace=True)
optuna_study_hgbc_pd.tail(5)

number  roc_train  roc_valid  f1_score  recall_1  precision_1  \
295     295   0.639844   0.626871  0.104007  0.127048     0.088040   
296     296   0.642986   0.626104  0.102226  0.130244     0.084129   
297     297   0.640274   0.626874  0.095783  0.090292     0.101986   
298     298   0.640450   0.625341  0.100633  0.114263     0.089909   
299     299   0.641138   0.624427  0.045771  0.027567     0.134766   

                datetime_start          datetime_complete  \
295 2025-04-18 00:36:47.370884 2025-04-18 00:36:59.400948   
296 2025-04-18 00:36:59.406620 2025-04-18 00:37:11.777817   
297 2025-04-18 00:37:11.783933 2025-04-18 00:37:23.667585   
298 2025-04-18 00:37:23.673799 2025-04-18 00:37:35.761533   
299 2025-04-18 00:37:35.767233 2025-04-18 00:37:47.519770   

                  duration  params_class_0_weight  ...  \
295 0 days 00:00:12.030064               0.264824  ...   
296 0 days 00:00:12.371197               0.234985  ...   
297 0 days 00:00:11.883652               0.286455  ...   
298 0 days 00:00:12.087734               0.584647  ...   
299 0 days 00:00:11.752537               0.512260  ...   

     params_l2_regularization  params_learning_rate  params_max_depth  \
295                  0.830355              0.099572                10   
296                  0.995115              0.096842                10   
297                  0.456242              0.099645                10   
298                  0.500533              0.057224                10   
299                  0.493191              0.097745                10   

     params_max_features  params_max_iter  params_max_leaf_nodes  \
295             0.998955              205                     38   
296             0.977023              208                     53   
297             0.673636              207                     50   
298             0.997937              210                     54   
299             0.990434              209                     52   

     params_min_samples_leaf  params_random_state  params_threshold     state  
295                       42               569646          0.943159  COMPLETE  
296                       39               541000          0.947638  COMPLETE  
297                       40               513953          0.941039  COMPLETE  
298                       41               600798          0.937810  COMPLETE  
299                       41               492564          0.889057  COMPLETE  

[5 rows x 22 columns]

In [1711]:
# покаждем статистику обучения
print('Максимальное значение метрики ROC AUC на валидационном наборе:',round(optuna_study_hgbc_pd['roc_valid'].max(),3))
print('Среднее значение метрики ROC AUC на валидационном наборе:',round(optuna_study_hgbc_pd['roc_valid'].mean(),3))
print('Максимальное значение метрики f1_score на валидационном наборе:',round(optuna_study_hgbc_pd['f1_score'].max(),3))
print('Среднее значение метрики f1_score на валидационном наборе:',round(optuna_study_hgbc_pd['f1_score'].mean(),3))
print('Максимальное значение метрики recall_1 на валидационном наборе:',round(optuna_study_hgbc_pd['recall_1'].max(),3))
print('Среднее значение метрики recall_1 на валидационном наборе:',round(optuna_study_hgbc_pd['recall_1'].mean(),3))
print('Максимальное значение метрики precision_1 на валидационном наборе:',round(optuna_study_hgbc_pd['precision_1'].max(),3))
print('Среднее значение метрики precision_1 на валидационном наборе:',round(optuna_study_hgbc_pd['precision_1'].mean(),3))

Максимальное значение метрики ROC AUC на валидационном наборе: 0.628
Среднее значение метрики ROC AUC на валидационном наборе: 0.626
Максимальное значение метрики f1_score на валидационном наборе: 0.112
Среднее значение метрики f1_score на валидационном наборе: 0.077
Максимальное значение метрики recall_1 на валидационном наборе: 1.0
Среднее значение метрики recall_1 на валидационном наборе: 0.308
Максимальное значение метрики precision_1 на валидационном наборе: 0.333
Среднее значение метрики precision_1 на валидационном наборе: 0.084


In [1713]:
# Построим зависимость метрик качества модели от number

fig = px.scatter(
    data_frame=optuna_study_hgbc_pd[(optuna_study_hgbc_pd['roc_valid']>0.999*optuna_study_hgbc_pd['roc_valid'].max())],
    x='number', #ось абсцисс
    y=['roc_train','roc_valid','recall_1','precision_1'], #ось ординат
)
fig.update_layout(
    title ={
        'text':'Зависимость качества модели от trials optuna', # Имя рабочей плоскости
        'font':{'size':35,'family':"Times New Roman"}, # размер и стиль написания имени рабочей плоскости
        'x':0.5, # Смешение имени по оси "x" на половину рабочей плоскости
        },
    height =800,# Высота рабочей плоскости
    width = 1350, # Ширина рабочей плоскости
    bargap=0.2, # Добавил расстояния между столбами гистограммы
    xaxis_title='trials optuna',
    yaxis_title='Величина параметра')
fig.update_xaxes(showspikes=True)
fig.update_yaxes(showspikes=True)

fig.show()

<span style="color:Blue">

Вывод:  

Их всех выбираем точку $number =205$.   
В этой точке оптимальные значения метрик $recall_1$ и $precision_1$, а  
также относительно высокая метрика $ROC AUC$.   
Посмотрим каким значениям гиперпараметров соотвествует выбранная точка.

In [1714]:
# определим номер лучшге варианта
best_optuna_number = 205

# сформируем словарь лучших гипирпарметров HistGradientBoostingClassifier
best_param_hgbc = {
    'learning_rate' : optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_learning_rate'].iloc[0],
    'max_iter' : optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_max_iter'].iloc[0],
    'max_leaf_nodes' : optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_max_leaf_nodes'].iloc[0],
    'max_depth' : optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_max_depth'].iloc[0],
    'min_samples_leaf' : optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_min_samples_leaf'].iloc[0],
    'max_features' : optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_max_features'].iloc[0],
    'l2_regularization' : optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_l2_regularization'].iloc[0],
    'class_weight' : {0: optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_class_0_weight'].iloc[0],
                      1: optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_class_1_weight'].iloc[0],}
    }

# определим перменные для лучших значений параметров
best_threshold = optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_threshold'].iloc[0]
best_class_1_percent = optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_class_1_percent'].iloc[0]
best_random_state = optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_random_state'].iloc[0]


# Выведем принятые наилучшие параметры
print('best learning rate:',round(best_param_hgbc['learning_rate'],3))
print('best max iter:',best_param_hgbc['max_iter'])
print('best max leaf nodes:',best_param_hgbc['max_leaf_nodes'])
print('best max depth:',best_param_hgbc['max_depth'])
print('best min samples leaf:',best_param_hgbc['min_samples_leaf'])
print('best max features:',round(best_param_hgbc['max_features'],3))
print('best l2 regularization:',round(best_param_hgbc['l2_regularization'],3))
print('best class 0 weight:',round(best_param_hgbc['class_weight'][0],3))
print('best class 1 weight:',round(best_param_hgbc['class_weight'][1],3))

print('best class 1 percent:',round(best_class_1_percent,3))
print('best threshold:',round(best_threshold,3))
print('time for best train:',round(optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['duration'].iloc[0].seconds/60),'minutes')

print()
print('ROC AUC на обучающем наборе:', round(optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['roc_train'].iloc[0],3))
print('ROC AUC на валидационном наборе:', round(optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['roc_valid'].iloc[0],3))
print('precision класса 1:', round(optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['precision_1'].iloc[0],3))
print('recall класса 1:', round(optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['recall_1'].iloc[0],3))

best learning rate: 0.068
best max iter: 216
best max leaf nodes: 32
best max depth: 10
best min samples leaf: 38
best max features: 0.715
best l2 regularization: 0.08
best class 0 weight: 0.559
best class 1 weight: 0.999
best class 1 percent: 0.123
best threshold: 0.936
time for best train: 0 minutes

ROC AUC на обучающем наборе: 0.636
ROC AUC на валидационном наборе: 0.627
precision класса 1: 0.167
recall класса 1: 0.02


##### <span style="color:MediumSlateBlue">Обучение модели с лучшими параметрами</span>

In [1715]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'late'
count_features = dict_spaces[feature_space]

# для работы функции corr_transform_to_force
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()

# с помощью функции corr_transform_to_force получим
# список не коррелируемых признаков
list_ncorr_features = corr_transform_to_force(corr_matrix,threshold=best_threshold)[1]

# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
y_train_pd = pd.read_csv('target/target_train.csv')

# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)

# подготовим данные для обучения модели
# с помощью функции class_1_percent_samples зададим долю 
# класса 1
list_c1_percent_id = class_1_percent_samples(y_train_pd,best_class_1_percent,random_state=best_random_state)[:1000000]

# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']

# освободим память от "тяжелых" и ненужных файлов
del X_train_pd, y_train_pd
gc.collect()

# обучаем модель HistGradientBoostingClassifier с наилучшеми параметрами
gradient_boosting = HistGradientBoostingClassifier(
        **best_param_hgbc,
        random_state=42)
gradient_boosting.fit(X_train_balanced,y_train_balanced)

# удаляем крупные файлы чтобы высвободить память 
del X_train_balanced, y_train_balanced
gc.collect()

# сформируем данные для анализа сбалансированности обучающих данных
X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()[list_ncorr_features]
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

# делаем предсказание на обучающем и валидационном наборе и считаем метрики
y_train_gb_pred_proba = gradient_boosting.predict_proba(X_train)[:,1]
y_valid_gb_pred_proba = gradient_boosting.predict_proba(X_valid)[:,1]
y_valid_gb_pred = gradient_boosting.predict(X_valid)

# удаляем крупные файлы чтобы высвободить память 
del X_train, X_valid
gc.collect()

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_gb_pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_gb_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_gb_pred,zero_division=0))

# time: 1m 40s

ROC AUC на обучающем наборе 0.636
ROC AUC на валидационном наборе 0.627
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.97      1.00      0.98     68747
           1       0.17      0.02      0.04      2503

    accuracy                           0.96     71250
   macro avg       0.57      0.51      0.51     71250
weighted avg       0.94      0.96      0.95     71250



### <span style="color:RoyalBlue">Построение модели на сбалансированных данных подпрострнства credit stat</span>

#### <span style="color:MediumBlue">Построение модели Logistic Regression</span>

##### <span style="color:MediumSlateBlue">Формирование данных для обучения</span>

Анализ исходных данных, в частности target, показал что представленные данные   
имееют перекос: 96% клиентов у которых не случился дефолт (flag = 0),    
против 4 % - для которых произошел дефолт (flag = 1).  
С помощью функции class_1_percent_samples, сформируем сбаланисрованную выборку  
для обучения моделей.
За основу сбалансировных данных возьмем данные клиентов с дефолтом  
и к ним будем добирать необходимое количество клиентов до сбалансированности. 


Функция class_1_percent_samples принемает две переменные:
- target_data - массив с id и целевой переменной
- class_1_percent - процент класса 1 в результирующем массиве

In [818]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'credit'
count_features = dict_spaces[feature_space]

In [819]:
# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

In [820]:
# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)
y_train_pd.head(4)

id  flag
id                    
1825800  1825800     0
2166483  2166483     0
2534345  2534345     0
1803283  1803283     0

In [821]:
# взглянем на сблансиорованность данных в y_train
y_train_pd['flag'].value_counts(normalize=True)

flag
0    0.964242
1    0.035758
Name: proportion, dtype: float64

In [822]:
# сбалансируем данные в y_train_pd
list_c1_percent_id = class_1_percent_samples(y_train_pd,0.5)
# list_c1_percent_features - список 'id' из y_train_pd соотвествующих  
# заданному проценту класса 1
len(list_c1_percent_id)

45860

In [823]:
# проверим сбалансированность полученного y_train
y_train_pd.loc[list_c1_percent_id]['flag'].value_counts(normalize=True)

flag
1    0.5
0    0.5
Name: proportion, dtype: float64

В отличие от данных в *transform_data_torow*, где модели показываеются последние N  
операций клиента, в данные в *transform_data_stat* сфомированы из различных статистических   
характеристик ряда определяющего клиентскую историю в банке. 

Соотвественно, если в данных *transform_data_torow* была сильная корреляция между признаками,  
то я не смог бы ее убрать, иначе потярется смысл "показать последовательный ряд в историии клиента".  
Признаки в *transform_data_stat* не имеют такой особенности. Поэтому, необходимо проанализировать  
данные в *transform_data_stat* и, в случае сильной коррреляции признаков, устранить ее.

In [824]:
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()
corr_matrix.shape

(69, 69)

In [825]:
# с помощью функции corr_transrom_to_power получим
# силу корреляции матрицы и список не коррелируемых признаков

# для начального анализа зададим порог силы корреляции, при котором признаки 
# будут отнесены к "сильно скоррелированными" равным 0.6
ncorr_matrix,list_ncorr_features,corr_power =corr_transform_to_force(corr_matrix,threshold=0.6)

# Выведем результаты преобразования
print('Исходное количество признаков: ', corr_matrix.shape[0])
print('Количество не коррелируемых признаков: ', len(list_ncorr_features))
# сила корреляции признаков
print('Отношение коррелируемых исходному количеству признаков (сила корреляции): ',corr_power)

Исходное количество признаков:  69
Количество не коррелируемых признаков:  24
Отношение коррелируемых исходному количеству признаков (сила корреляции):  0.652


In [826]:
# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']
# сформируем данные для проверики модели
# сформируем данные для анализа сбалансированности обучающих данных
X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()
y_train = pd.read_csv('target/target_train.csv')['flag']
X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()
y_valid = pd.read_csv('target/target_valid.csv')['flag']

In [827]:
# посмотрим на структуру данных в X_train_balanced
X_train_balanced.head(4)

f1    f2      f3     f4     f5      f6      f7   f8     f9  f10  \
id                                                                           
2335465  17.0  19.0  10.824  0.000  0.000  18.464  10.824  0.0  7.246  0.0   
390270    6.0  17.0  10.167  8.165  8.165  18.331  10.167  0.0  5.520  2.0   
2494034  14.0  16.0  10.643  8.958  8.958  18.276  10.643  0.0  5.702  3.0   
2018674  15.0  19.0  10.333  0.000  0.000  18.022  10.333  0.0  6.529  0.0   

         ...    f60  f61  f62  f63  f64   f65  f66   f67     f68  f69  
id       ...                                                           
2335465  ...  3.291  1.0  2.0  3.0  5.4  13.0  2.0  0.29  11.507  7.0  
390270   ...  1.700  0.0  1.0  2.5  4.0   4.0  4.0  0.50   3.467  2.0  
2494034  ...  3.731  0.0  4.0  4.0  4.3  13.0  4.0  0.64  14.989  6.5  
2018674  ...  3.197  0.0  2.0  2.0  2.0  11.0  2.0  0.67  10.952  5.5  

[4 rows x 69 columns]

In [828]:
# посмотрим на структуру данных в y_train_balanced
y_train_balanced.head(4)

id
2335465    1
390270     1
2494034    1
2018674    1
Name: flag, dtype: int64

In [829]:
# проверим что выборки действительно совпадают по id
X_train_balanced.index.to_list() == y_train_balanced.index.to_list()

True

##### <span style="color:MediumSlateBlue">Baseline обучение модели LogisticRegression</span>

In [830]:
# обучаем модель логистической регрессии
logistic_regression = linear_model.LogisticRegression(random_state=42, max_iter=10000)
logistic_regression.fit(X_train_balanced[list_ncorr_features],y_train_balanced)

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_LR_pred_proba = logistic_regression.predict_proba(X_train[list_ncorr_features])[:,1]
y_valid_LR_pred_proba = logistic_regression.predict_proba(X_valid[list_ncorr_features])[:,1]

# Делаем предсказание для валидационной выборки
y_valid_LR_pred = logistic_regression.predict(X_valid[list_ncorr_features])

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_LR_pred_proba),3))
print('ROC AUC на тестовом наборе', round(metrics.roc_auc_score(y_valid, y_valid_LR_pred_proba),3))

print('Основные метрики на тестовом наборе:')
print(metrics.classification_report(y_valid,y_valid_LR_pred))

# time: 3m 5s

ROC AUC на обучающем наборе 0.583
ROC AUC на тестовом наборе 0.584
Основные метрики на тестовом наборе:
              precision    recall  f1-score   support

           0       0.97      0.60      0.74     68747
           1       0.05      0.52      0.08      2503

    accuracy                           0.59     71250
   macro avg       0.51      0.56      0.41     71250
weighted avg       0.94      0.59      0.72     71250



##### <span style="color:MediumSlateBlue">Анализ влияния scaler преобразования на качество и скорость схождения модели</span>

In [831]:
# формируем список из необходимых scaler
scalers = [MinMaxScaler(),RobustScaler() ,StandardScaler()]

# сформируем списко для заполнения данными результатов анализа
scalers_data = []

# установим ограничение на время обучения модели в 600 секунд (10 минут)
time_out = 600

for scaler in scalers:
        # для того чтобы следить за выполнением цикла введем индикатор
        print('current scaler: ', scaler)

         # сформируем список для заполнения данными текушего scaler
        current_scaler_data = [scaler]
        
        # выполним scaler преобразование
        X_train_s_balanced = scaler.fit_transform(X_train_balanced[list_ncorr_features])
        X_train_s = scaler.transform(X_train[list_ncorr_features])
        X_valid_s = scaler.transform(X_valid[list_ncorr_features])

        try:
                # для модуля func_time_out упакуем обучение модели в функцию try_func
                def try_func():
                        logistic_regression = linear_model.LogisticRegression(random_state=42, max_iter=10000)
                        return logistic_regression.fit(X_train_s_balanced,y_train_balanced)
                    
                # фиксируем время начала
                start_time = time.time()
                
                # запускаем обучение модели с ограничением по времени
                logistic_regression = func_timeout.func_timeout(time_out, try_func)
                
                # фиксируем время окончания обучения
                end_time = time.time()
                
                # запишем время обучения модели
                current_scaler_data.append(round(end_time-start_time))

                # Делаем предсказание для обучающей и валидационной выборки
                y_valid_lr_pred = logistic_regression.predict(X_valid_s)
                
                # для метрик ROC AUC делаем предсказание модели для обучающей и валидационной выборки  
                # в виде вероятности принадлежности к классу 1 
                y_train_lr_pred_proba = logistic_regression.predict_proba(X_train_s)[:,1]
                y_valid_lr_pred_proba = logistic_regression.predict_proba(X_valid_s)[:,1]

                #Считаем метрики ROC AUC yна обуающем и валидационном наборе и добавляем их в спискок
                current_scaler_data.append(round(metrics.roc_auc_score(y_train, y_train_lr_pred_proba),3))
                current_scaler_data.append(round(metrics.roc_auc_score(y_valid, y_valid_lr_pred_proba),3))

                #Считаем метрики для класса 0 на валидационном наборе и добавляем их в список
                current_scaler_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))
                current_scaler_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))


                #Считаем метрики для класса 1 на валидационном набопе и добавляем их в список
                current_scaler_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))
                current_scaler_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))

                # добавляем полученные данные в список scalers_data
                scalers_data.append(current_scaler_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                scaler_pd =pd.DataFrame(
                        columns=['scaler','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = scalers_data)
                # сохраняем dataframe
                scaler_pd.to_csv('data_recovery/scaler_pd.csv',index=False)
               
                # очистим output от прошедшей итерации
                clear_output()

        except func_timeout.FunctionTimedOut:
                # если время обучения привышает лимит
                # запишем в current_scaler_data соотвествующую данные
                current_scaler_data = [scaler,'>30m',0,0,0,0,0,0]
                # добавляем полученные данные в список scalers_data
                scalers_data.append(current_scaler_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                scaler_pd =pd.DataFrame(
                        columns=['scaler','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = scalers_data)
                # сохраняем dataframe
                scaler_pd.to_csv('data_recovery/scaler_pd.csv',index=False)
                
                # очистим output от прошедшей итерации
                clear_output()
                # переходим к следующему scaler
                pass
# очистим output
clear_output()

# сформируем данные соотвествующие лучщему ROC AUC на валидацинном наборе
best_roc_valid_data = scaler_pd[scaler_pd['roc_valid']==scaler_pd['roc_valid'].max()]

# выведем лучший результат на валидационном наборе
print('result:')
print('best scaler on valid:',best_roc_valid_data.iloc[0]['scaler'])
print('ROC AUC on train:', best_roc_valid_data.iloc[0]['roc_train'])
print('ROC AUC on valid:', best_roc_valid_data.iloc[0]['roc_valid'])
print('Time fit for best scaler:', best_roc_valid_data.iloc[0]['time_fit'],' seconds')

# выведем полученный dataframe
scaler_pd

# time: 

result:
best scaler on valid: RobustScaler()
ROC AUC on train: 0.583
ROC AUC on valid: 0.584
Time fit for best scaler: 0  seconds


scaler  time_fit  roc_train  roc_valid  recall_0  precision_0  \
0    MinMaxScaler()         0      0.583      0.583     0.597        0.972   
1    RobustScaler()         0      0.583      0.584     0.596        0.972   
2  StandardScaler()         0      0.583      0.584     0.596        0.972   

   recall_1  precision_1  
0     0.526        0.045  
1     0.525        0.045  
2     0.524        0.045

##### <span style="color:MediumSlateBlue"> Анализ влияния solver оптимизатора на качество и скорость обучения модели</span>

Проверим качество и скорость сходимости модели при разных solver  
Проверку осуществим через цикл  
Чтобы модель не сходилась бесконечно с помощью модуля func_timeout  
поставим ограничение времени схождения в 10 минут

In [832]:
# подготовим данные для обучения модели

# обьявим scaler
scaler = StandardScaler()
# выполним scaler преобразование
X_train_s_balanced = scaler.fit_transform(X_train_balanced[list_ncorr_features])
X_train_s = scaler.transform(X_train[list_ncorr_features])
X_valid_s = scaler.transform(X_valid[list_ncorr_features])

# time: 10s

In [833]:
# Зададим список solvers
solvers_list = ['lbfgs', 'liblinear', 'newton-cg', 'newton-cholesky', 'sag', 'saga']

# сформируем список для заполнения
solvers_data = []

# установим ограничение на время обучения модели в 180 секунд (3 минут)
time_out = 180

for solver in solvers_list:
        # для того чтобы следить за выполнением цикла введем индикатор
        print('current solver: ', solver)

         # сформируем список для заполнения данными текушего solver
        current_solver_data = [solver]
        
        try:
                # для модуля func_time_out упакуем обучение модели в функцию try_func
                def try_func():
                        logistic_regression = linear_model.LogisticRegression(solver= solver,
                                                                  random_state=42, 
                                                                  max_iter=10000)
                        return logistic_regression.fit(X_train_s_balanced,y_train_balanced)
                    
                # фиксируем время начала
                start_time = time.time()
                
                # запускаем обучение модели с ограничением по времени
                logistic_regression = func_timeout.func_timeout(time_out, try_func)
                
                # фиксируем время окончания обучения
                end_time = time.time()
                
                # запишем время обучения модели
                current_solver_data.append(round(end_time-start_time))

                # Делаем предсказание для обучающей и валидационной выборки
                y_valid_lr_pred = logistic_regression.predict(X_valid_s)
                
                # для метрик ROC AUC делаем предсказание модели для обучающей и валидационной выборки  
                # в виде вероятности принадлежности к классу 1 
                y_train_lr_pred_proba = logistic_regression.predict_proba(X_train_s)[:,1]
                y_valid_lr_pred_proba = logistic_regression.predict_proba(X_valid_s)[:,1]

                #Считаем метрики ROC AUC yна обуающем и валидационном наборе и добавляем их в спискок
                current_solver_data.append(round(metrics.roc_auc_score(y_train, y_train_lr_pred_proba),3))
                current_solver_data.append(round(metrics.roc_auc_score(y_valid, y_valid_lr_pred_proba),3))

                #Считаем метрики для класса 0 на валидационном наборе и добавляем их в список
                current_solver_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))
                current_solver_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))


                #Считаем метрики для класса 1 на валидационном набопе и добавляем их в список
                current_solver_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))
                current_solver_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))

                # запишем данные полученные на одной итерации
                solvers_data.append(current_solver_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                solvers_pd =pd.DataFrame(
                        columns=['solver','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = solvers_data)
                # сохраняем dataframe
                solvers_pd.to_csv('data_recovery/solvers_pd.csv',index=False)
               
                # очистим output от прошедшей итерации
                clear_output()

        except func_timeout.FunctionTimedOut:
                # если время обучения привышает лимит
                # запишем в current_solver_data соотвествующую данные
                current_solver_data = [solver,'>3m',0,0,0,0,0,0]
                # добавляем полученные данные в список solvers_data
                solvers_data.append(current_solver_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                solvers_pd =pd.DataFrame(
                        columns=['solver','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = solvers_data)
                # сохраняем dataframe
                solvers_pd.to_csv('data_recovery/solvers_pd.csv',index=False)
                
                # очистим output от прошедшей итерации
                clear_output()
                # переходим к следующему solver
                pass
# очистим output
clear_output()

# сформируем данные соотвествующие лучщему ROC AUC на валидацинном наборе
best_roc_valid_data = solvers_pd[solvers_pd['roc_valid']==solvers_pd['roc_valid'].max()]

# выведем лучший результат на валидационном наборе
print('result:')
print('best solver on valid:',best_roc_valid_data.iloc[0]['solver'])
print('ROC AUC on train:', best_roc_valid_data.iloc[0]['roc_train'])
print('ROC AUC on valid:', best_roc_valid_data.iloc[0]['roc_valid'])
print('Time fit for best solver:', best_roc_valid_data.iloc[0]['time_fit'],' seconds')

# выведем полученный dataframe
solvers_pd

# time: 2m 35s

result:
best solver on valid: lbfgs
ROC AUC on train: 0.583
ROC AUC on valid: 0.584
Time fit for best solver: 0  seconds


solver  time_fit  roc_train  roc_valid  recall_0  precision_0  \
0            lbfgs         0      0.583      0.584     0.596        0.972   
1        liblinear         0      0.583      0.584     0.596        0.972   
2        newton-cg         0      0.583      0.584     0.596        0.972   
3  newton-cholesky         0      0.583      0.584     0.596        0.972   
4              sag         0      0.583      0.584     0.596        0.972   
5             saga         0      0.583      0.584     0.596        0.972   

   recall_1  precision_1  
0     0.524        0.045  
1     0.524        0.045  
2     0.524        0.045  
3     0.524        0.045  
4     0.524        0.045  
5     0.524        0.045

##### <span style="color:MediumSlateBlue">Подбор гиперпараметров модели</span>

In [1716]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'credit'
count_features = dict_spaces[feature_space]

# для работы функции corr_transform_to_force
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()

# для выбора sceler преобразвания нам понадобится словарь
dict_scalers ={
    'MinMaxScaler': MinMaxScaler(),
    'RobustScaler':RobustScaler(),
    'StandardScaler':StandardScaler()}

# настроим оптимизацию гипер параметров
def optuna_lg(trial):
  # задаем пространства поиска гиперпараметров
  solver = trial.suggest_categorical("solver", ['lbfgs', 'liblinear', 'newton-cg', 'newton-cholesky'])
  C = trial.suggest_float('C',0.01,1)
  class_0_weight = trial.suggest_float('class_0_weight',0.2,0.6)
  class_1_weight = trial.suggest_float('class_1_weight',0.2,0.6)
  threshold = trial.suggest_float('threshold',0.6,1)
  class_1_percent = trial.suggest_float('class_1_percent',0.01,0.3)
  scaler = trial.suggest_categorical("scaler", ['MinMaxScaler','RobustScaler','StandardScaler'])
  random_state = trial.suggest_int('random_state', 1, 1000000)


  # создаем модель
  optuna_log_reg = linear_model.LogisticRegression(
      solver=solver,
      C=C,
      class_weight={0:class_0_weight,1:class_1_weight},
      random_state=random_state,
      max_iter=10000)

  # с помощью функции corr_transform_to_force получим
  # список не коррелируемых признаков
  list_ncorr_features = corr_transform_to_force(corr_matrix,threshold=threshold)[1]

  # обьявим scaler
  scaler = dict_scalers[scaler]

  # сформируем данные для анализа сбалансированности обучающих данных
  X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
  y_train_pd = pd.read_csv('target/target_train.csv')

  # поготовим данные y_train_pd к работе с функцией class_1_percent_samples
  y_train_pd.set_index('id',drop=False,inplace=True)

  # подготовим данные для обучения модели
  # с помощью функции class_1_percent_samples зададим долю 
  # класса 1
  list_c1_percent_id = class_1_percent_samples(y_train_pd,class_1_percent,random_state=random_state)[:1000000]

  # подготовим данные для обучения
  X_train_s_balanced = scaler.fit_transform(X_train_pd.loc[list_c1_percent_id])
  y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

  # освободим память от "тяжелых" и ненужных файлов
  del X_train_pd, y_train_pd
  gc.collect()

  # я не воспользовался параметром timeout метода optimize потому, что  
  # optimize отставливает поиск параметров, если время обучения 
  # превышает timeout. Мне нужно чтобы поиск параметров продолжился.
  try:
    # для модуля func_time_out упакуем обучение модели в функцию try_func
    def try_func():
            return optuna_log_reg.fit(X_train_s_balanced, y_train_balanced)
    # обучаем модель с ограничением по времени 10 минут (600 секунд)
    optuna_log_reg = func_timeout.func_timeout(600, try_func)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train_s_balanced, y_train_balanced
    gc.collect()

    # загружаем тестовые наборы
    # сформируем данные для анализа сбалансированности обучающих данных
    X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
    X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()[list_ncorr_features]
    y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
    y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

    # подготовим данные для проверки модели
    X_train_s = scaler.transform(X_train)
    X_valid_s = scaler.transform(X_valid)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train, X_valid
    gc.collect()

    # делаем предсказание на обучающем и валидационном наборе и считаем метрики
    roc_train = metrics.roc_auc_score(y_train, optuna_log_reg.predict_proba(X_train_s)[:,1])
    roc_valid = metrics.roc_auc_score(y_valid, optuna_log_reg.predict_proba(X_valid_s)[:,1])
    f1_score = metrics.f1_score(y_valid, optuna_log_reg.predict(X_valid_s))
    recall_1 = metrics.recall_score(y_valid, optuna_log_reg.predict(X_valid_s),average=None,zero_division=0)[1]
    precision_1 = metrics.precision_score(y_valid, optuna_log_reg.predict(X_valid_s),average=None,zero_division=0)[1]

    # удаляем крупные файлы чтобы высвободить память 
    del X_train_s, X_valid_s, y_train, y_valid
    gc.collect()

  except func_timeout.FunctionTimedOut:
    # удаляем крупные файлы чтобы высвободить память 
    del X_train_s_balanced, y_train_balanced
    gc.collect()
    
    # фиксируем пустые значения метрик
    roc_train = 0
    roc_valid = 0
    f1_score = 0
    recall_1 = 0
    precision_1 = 0
    pass

  return roc_train, roc_valid, f1_score, recall_1, precision_1

In [1717]:
# cоздаем объект исследования
# чтобы модель не переобучалась минимизируем roc_train 
# и максимизируем roc_valid
optuna_study_lg = optuna.create_study(study_name='LogisticRegression_'+feature_space+'_stat', 
                               directions=['maximize','maximize','maximize','maximize','maximize'], 
                               sampler=optuna.samplers.TPESampler(),
                               pruner='Hyperband',
                               storage='sqlite:///optuna_studies.db',
                               load_if_exists=True)
# optuna.delete_study(study_name='LogisticRegression_'+feature_space+'_stat', storage='sqlite:///optuna_studies.db')

[I 2025-04-19 14:48:00,767] Using an existing study with name 'LogisticRegression_credit_stat' instead of creating a new one.


In [836]:
# ищем лучшую комбинацию гиперпараметров n_trials раз
optuna_study_lg.optimize(optuna_lg, n_trials=300)

[I 2025-04-18 00:38:23,685] Trial 0 finished with values: [0.5845578065534075, 0.5851035516220922, 0.0, 0.0, 0.0] and parameters: {'solver': 'lbfgs', 'C': 0.7643633457621303, 'class_0_weight': 0.5594464719771861, 'class_1_weight': 0.2672701123651094, 'threshold': 0.6490237057334364, 'class_1_percent': 0.26217563059057636, 'scaler': 'StandardScaler', 'random_state': 784807}.
[I 2025-04-18 00:38:28,663] Trial 1 finished with values: [0.5941782249802329, 0.5953862361834743, 0.0, 0.0, 0.0] and parameters: {'solver': 'liblinear', 'C': 0.10958497231697518, 'class_0_weight': 0.3605471957024974, 'class_1_weight': 0.2525700687599625, 'threshold': 0.9272140793168333, 'class_1_percent': 0.22126181702051953, 'scaler': 'MinMaxScaler', 'random_state': 39223}.
[I 2025-04-18 00:38:33,863] Trial 2 finished with values: [0.5967593670103766, 0.5991016897807784, 0.0, 0.0, 0.0] and parameters: {'solver': 'newton-cg', 'C': 0.6422026242622605, 'class_0_weight': 0.3292575834946739, 'class_1_weight': 0.3486589

In [1718]:
# из полученного результат соврмируем Data Frame
optuna_study_lg_pd = optuna_study_lg.trials_dataframe().dropna()
# переименуем столбы
optuna_study_lg_pd.rename(columns={
    'values_0': 'roc_train',
    'values_1': 'roc_valid',
    'values_2': 'f1_score',
    'values_3': 'recall_1',
    'values_4': 'precision_1'
},inplace=True)
# Выделим время потраченное на обучение модели
optuna_study_lg_pd.tail()

number  roc_train  roc_valid  f1_score  recall_1  precision_1  \
295     295   0.599833   0.602838  0.003948  0.001998     0.166667   
296     296   0.600515   0.604312  0.086296  0.576508     0.046639   
297     297   0.600424   0.605357  0.000000  0.000000     0.000000   
298     298   0.581365   0.580220  0.000000  0.000000     0.000000   
299     299   0.600839   0.603737  0.089811  0.204954     0.057505   

                datetime_start          datetime_complete  \
295 2025-04-18 01:06:58.354578 2025-04-18 01:07:05.627585   
296 2025-04-18 01:07:05.632964 2025-04-18 01:07:12.637125   
297 2025-04-18 01:07:12.642739 2025-04-18 01:07:20.054548   
298 2025-04-18 01:07:20.060224 2025-04-18 01:07:26.974424   
299 2025-04-18 01:07:26.979940 2025-04-18 01:07:33.857993   

                  duration  params_C  params_class_0_weight  \
295 0 days 00:00:07.273007  0.350705               0.225879   
296 0 days 00:00:07.004161  0.272580               0.212015   
297 0 days 00:00:07.411809  0.251130               0.406419   
298 0 days 00:00:06.914200  0.316780               0.244122   
299 0 days 00:00:06.878053  0.208003               0.234050   

     params_class_1_percent  params_class_1_weight  params_random_state  \
295                0.123600               0.584313               299187   
296                0.271814               0.560425               441482   
297                0.230351               0.211026               697950   
298                0.046592               0.525065               489982   
299                0.215903               0.597863               504862   

      params_scaler params_solver  params_threshold     state  
295    MinMaxScaler     newton-cg          0.984759  COMPLETE  
296  StandardScaler         lbfgs          0.993584  COMPLETE  
297  StandardScaler     liblinear          0.967571  COMPLETE  
298  StandardScaler         lbfgs          0.667981  COMPLETE  
299  StandardScaler     newton-cg          0.976955  COMPLETE

In [1719]:
# покаждем статистику обучения
print('Максимальное значение метрики ROC AUC на валидационном наборе:',round(optuna_study_lg_pd['roc_valid'].max(),3))
print('Среднее значение метрики ROC AUC на валидационном наборе:',round(optuna_study_lg_pd['roc_valid'].mean(),3))
print('Максимальное значение метрики f1_score на валидационном наборе:',round(optuna_study_lg_pd['f1_score'].max(),3))
print('Среднее значение метрики f1_score на валидационном наборе:',round(optuna_study_lg_pd['f1_score'].mean(),3))
print('Максимальное значение метрики recall_1 на валидационном наборе:',round(optuna_study_lg_pd['recall_1'].max(),3))
print('Среднее значение метрики recall_1 на валидационном наборе:',round(optuna_study_lg_pd['recall_1'].mean(),3))
print('Максимальное значение метрики precision_1 на валидационном наборе:',round(optuna_study_lg_pd['precision_1'].max(),3))
print('Среднее значение метрики precision_1 на валидационном наборе:',round(optuna_study_lg_pd['precision_1'].mean(),3))

Максимальное значение метрики ROC AUC на валидационном наборе: 0.606
Среднее значение метрики ROC AUC на валидационном наборе: 0.6
Максимальное значение метрики f1_score на валидационном наборе: 0.096
Среднее значение метрики f1_score на валидационном наборе: 0.054
Максимальное значение метрики recall_1 на валидационном наборе: 0.659
Среднее значение метрики recall_1 на валидационном наборе: 0.176
Максимальное значение метрики precision_1 на валидационном наборе: 0.25
Среднее значение метрики precision_1 на валидационном наборе: 0.054


In [1722]:
# Визуализируем метрики полученные при optuna оптимизации
fig = px.scatter(
    data_frame=optuna_study_lg_pd[(optuna_study_lg_pd['roc_valid']>0.999*(optuna_study_lg_pd['roc_valid'].max()))],
    x='number', #ось абсцисс
    y=['roc_train','roc_valid','recall_1','precision_1'], #ось ординат
)
fig.update_layout(
    title ={
        'text':'Зависимость качества модели от trials optuna', # Имя рабочей плоскости
        'font':{'size':35,'family':"Times New Roman"}, # размер и стиль написания имени рабочей плоскости
        'x':0.5, # Смешение имени по оси "x" на половину рабочей плоскости
        },
    height =800,# Высота рабочей плоскости
    width = 1350, # Ширина рабочей плоскости
    bargap=0.2, # Добавил расстояния между столбами гистограммы
    xaxis_title='trials optuna',
    yaxis_title='Величина метрики')
fig.update_xaxes(showspikes=True)
fig.update_yaxes(showspikes=True)

fig.show()

<span style="color:Blue">

Вывод:  

Их всех выбираем точку $number =235$.   
В этой точке самые оптимальные значения $recall$ и $precision$.  
Посмотрим каким значениям гиперпараметров соотвествует выбранная точка.

In [1723]:
# определим номер лучшге варианта
best_optuna_number = 235

# сформируем словарь лучших гипирпарметров RandomForestClassifier
best_param_lr = {
    'solver' : optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_solver'].iloc[0],
    'C' : round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_C'].iloc[0],3),
    'class_weight' : {0:round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_class_0_weight'].iloc[0],3),
                      1:round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_class_1_weight'].iloc[0],3)},
    }

# создадим перменные
best_threshold = optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_threshold'].iloc[0]
best_scaler = optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_scaler'].iloc[0]
best_class_1_percent = optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_class_1_percent'].iloc[0]
best_random_state = optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_random_state'].iloc[0]

# Выведем принятые наилучшие праметры
print('best solver:',best_param_lr['solver'])
print('best C:',best_param_lr['C'])
print('best class 0 weight:',best_param_lr['class_weight'][0])
print('best class 1 weight:',best_param_lr['class_weight'][1])

print('best class 1 percent:',round(best_class_1_percent,3))
print('best scaler:',best_scaler)
print('best threshold:',round(best_threshold,3))
print('best best random state:',best_random_state)
print('time for best train:',round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['duration'].iloc[0].seconds/60),'minutes')

print()
print('ROC AUC на обучающем наборе:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['roc_train'].iloc[0],3))
print('ROC AUC на валидационном наборе:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['roc_valid'].iloc[0],3))
print('precision класса 1:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['precision_1'].iloc[0],3))
print('recall класса 1:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['recall_1'].iloc[0],3))


best solver: newton-cg
best C: 0.328
best class 0 weight: 0.227
best class 1 weight: 0.551
best class 1 percent: 0.144
best scaler: StandardScaler
best threshold: 0.999
best best random state: 748183
time for best train: 0 minutes

ROC AUC на обучающем наборе: 0.602
ROC AUC на валидационном наборе: 0.606
precision класса 1: 0.115
recall класса 1: 0.009


##### <span style="color:MediumSlateBlue">Обучение модели с лучшими параметрами</span>

In [1724]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'credit'
count_features = dict_spaces[feature_space]

# для работы функции corr_transform_to_force
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()

# подготовим данные
# для выбора sceler преобразвания нам понадобится словарь
dict_scalers ={
    'MinMaxScaler': MinMaxScaler(),
    'RobustScaler':RobustScaler(),
    'StandardScaler':StandardScaler(),
}

# с помощью функции corr_transform_to_force получим
# список не коррелируемых признаков
list_ncorr_features = corr_transform_to_force(corr_matrix,threshold=best_threshold)[1]

# обьявим scaler
scaler = dict_scalers[best_scaler]

# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
y_train_pd = pd.read_csv('target/target_train.csv')

# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)

# подготовим данные для обучения модели
# с помощью функции class_1_percent_samples зададим долю 
# класса 1
list_c1_percent_id = class_1_percent_samples(y_train_pd,best_class_1_percent,random_state=best_random_state)[:1000000]

# подготовим данные для обучения
X_train_s_balanced = scaler.fit_transform(X_train_pd.loc[list_c1_percent_id])
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

# освободим память от "тяжелых" и ненужных файлов
del X_train_pd, y_train_pd
gc.collect()


# обучаем модель LogisticRegression с наилучшеми параметрами
logistic_regression = linear_model.LogisticRegression(
        **best_param_lr,
        random_state=42,
        max_iter=10000)
logistic_regression.fit(X_train_s_balanced, y_train_balanced)

# удаляем крупные файлы чтобы высвободить память 
del X_train_s_balanced, y_train_balanced
gc.collect()

# загружаем тестовые наборы
# сформируем данные для анализа сбалансированности обучающих данных
X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()[list_ncorr_features]
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

# подготовим данные для проверки модели
X_train_s = scaler.transform(X_train)
X_valid_s = scaler.transform(X_valid)

# удаляем крупные файлы чтобы высвободить память 
del X_train, X_valid
gc.collect()

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_lr_pred_proba = logistic_regression.predict_proba(X_train_s)[:,1]
y_valid_lr_pred_proba = logistic_regression.predict_proba(X_valid_s)[:,1]

# Делаем предсказание для валидационной выборки
y_valid_lr_pred = logistic_regression.predict(X_valid_s)

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_lr_pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_lr_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_lr_pred,zero_division=0))

# time: 2m 30s

ROC AUC на обучающем наборе 0.602
ROC AUC на валидационном наборе 0.606
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.97      1.00      0.98     68747
           1       0.12      0.01      0.02      2503

    accuracy                           0.96     71250
   macro avg       0.54      0.50      0.50     71250
weighted avg       0.94      0.96      0.95     71250



#### <span style="color:MediumBlue">Построение модели Random Forest Classifier</span>

##### <span style="color:MediumSlateBlue">Формирование данных для обучения</span>

Анализ исходных данных, в частности target, показал что представленные данные   
имееют перекос: 96% клиентов у которых не случился дефолт (flag = 0),    
против 4 % - для которых произошел дефолт (flag = 1).  
С помощью функции class_1_percent_samples, сформируем сбаланисрованную выборку  
для обучения моделей.
За основу сбалансировных данных возьмем данные клиентов с дефолтом  
и к ним будем добирать необходимое количество клиентов до сбалансированности. 


Функция class_1_percent_samples принемает две переменные:
- target_data - массив с id и целевой переменной
- class_1_percent - процент класса 1 в результирующем массиве

In [854]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'credit'
count_features = dict_spaces[feature_space]

In [855]:
# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

In [856]:
# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)
y_train_pd.head(4)

id  flag
id                    
1825800  1825800     0
2166483  2166483     0
2534345  2534345     0
1803283  1803283     0

In [857]:
# взглянем на сблансиорованность данных в y_train
y_train_pd['flag'].value_counts(normalize=True)

flag
0    0.964242
1    0.035758
Name: proportion, dtype: float64

In [858]:
# сбалансируем данные в y_train_pd
list_c1_percent_id = class_1_percent_samples(y_train_pd,0.5)
# list_c1_percent_features - список 'id' из y_train_pd соотвествующих  
# заданному проценту класса 1
len(list_c1_percent_id)

45860

In [859]:
# проверим сбалансированность полученного y_train
y_train_pd.loc[list_c1_percent_id]['flag'].value_counts(normalize=True)

flag
1    0.5
0    0.5
Name: proportion, dtype: float64

В отличие от данных в *transform_data_torow*, где модели показываеются последние N  
операций клиента, в данные в *transform_data_stat* сфомированы из различных статистических   
характеристик ряда определяющего клиентскую историю в банке. 

Соотвественно, если в данных *transform_data_torow* была сильная корреляция между признаками,  
то я не смог бы ее убрать, иначе потярется смысл "показать последовательный ряд в историии клиента".  
Признаки в *transform_data_stat* не имеют такой особенности. Поэтому, необходимо проанализировать  
данные в *transform_data_stat* и, в случае сильной коррреляции признаков, устранить ее.

In [860]:
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()
corr_matrix.shape

(69, 69)

In [861]:
# с помощью функции corr_transrom_to_power получим
# силу корреляции матрицы и список не коррелируемых признаков

# для начального анализа зададим порог силы корреляции, при котором признаки 
# будут отнесены к "сильно скоррелированными" равным 0.6
ncorr_matrix,list_ncorr_features,corr_power =corr_transform_to_force(corr_matrix,threshold=0.6)

# Выведем результаты преобразования
print('Исходное количество признаков: ', corr_matrix.shape[0])
print('Количество не коррелируемых признаков: ', len(list_ncorr_features))
# сила корреляции признаков
print('Отношение коррелируемых исходному количеству признаков (сила корреляции): ',corr_power)

Исходное количество признаков:  69
Количество не коррелируемых признаков:  24
Отношение коррелируемых исходному количеству признаков (сила корреляции):  0.652


In [862]:
# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']
# сформируем данные для проверики модели
# сформируем данные для анализа сбалансированности обучающих данных
X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()
y_train = pd.read_csv('target/target_train.csv')['flag']
X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()
y_valid = pd.read_csv('target/target_valid.csv')['flag']

In [863]:
# посмотрим на структуру данных в X_train_balanced
X_train_balanced.head(4)

f1    f2      f3     f4     f5      f6      f7   f8     f9  f10  \
id                                                                           
2335465  17.0  19.0  10.824  0.000  0.000  18.464  10.824  0.0  7.246  0.0   
390270    6.0  17.0  10.167  8.165  8.165  18.331  10.167  0.0  5.520  2.0   
2494034  14.0  16.0  10.643  8.958  8.958  18.276  10.643  0.0  5.702  3.0   
2018674  15.0  19.0  10.333  0.000  0.000  18.022  10.333  0.0  6.529  0.0   

         ...    f60  f61  f62  f63  f64   f65  f66   f67     f68  f69  
id       ...                                                           
2335465  ...  3.291  1.0  2.0  3.0  5.4  13.0  2.0  0.29  11.507  7.0  
390270   ...  1.700  0.0  1.0  2.5  4.0   4.0  4.0  0.50   3.467  2.0  
2494034  ...  3.731  0.0  4.0  4.0  4.3  13.0  4.0  0.64  14.989  6.5  
2018674  ...  3.197  0.0  2.0  2.0  2.0  11.0  2.0  0.67  10.952  5.5  

[4 rows x 69 columns]

In [864]:
# посмотрим на структуру данных в y_train_balanced
y_train_balanced.head(4)

id
2335465    1
390270     1
2494034    1
2018674    1
Name: flag, dtype: int64

In [865]:
# проверим что выборки действительно совпадают по id
X_train_balanced.index.to_list() == y_train_balanced.index.to_list()

True

##### <span style="color:MediumSlateBlue">Baseline обучение модели RandomForestClassifier</span>

In [866]:
# обучаем модель логистической регрессии
# чтобы модель пыталась найти связь во всех признаках
random_forest = RandomForestClassifier(random_state=42, n_jobs=-1)
random_forest.fit(X_train_balanced[list_ncorr_features],y_train_balanced)

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_rf__pred_proba = random_forest.predict_proba(X_train[list_ncorr_features])[:,1]
y_valid_rf_pred_proba = random_forest.predict_proba(X_valid[list_ncorr_features])[:,1]

# Делаем предсказание для валидационной выборки
y_valid_rf_pred = random_forest.predict(X_valid[list_ncorr_features])

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_rf__pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_rf_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_rf_pred))

# time: 17s

ROC AUC на обучающем наборе 0.963
ROC AUC на валидационном наборе 0.618
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.97      0.61      0.75     68747
           1       0.05      0.57      0.09      2503

    accuracy                           0.61     71250
   macro avg       0.51      0.59      0.42     71250
weighted avg       0.94      0.61      0.73     71250



##### <span style="color:MediumSlateBlue">Подбор гиперпараметров модели</span>

In [1725]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'credit'
count_features = dict_spaces[feature_space]

# для работы функции corr_transform_to_force
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()

# настроим оптимизацию гипер параметров
def optuna_rf(trial):
  # задаем пространства поиска гиперпараметров
  # задаем пространства поиска гиперпараметров
  n_estimators = trial.suggest_int('n_estimators', 40, 100,step = 5)
  criterion = trial.suggest_categorical('criterion',['gini', 'entropy', 'log_loss'])
  max_depth = trial.suggest_int('max_depth', 10, 30,step = 1)
  min_samples_split = trial.suggest_int('min_samples_split', 5, 15,step = 1)
  min_samples_leaf = trial.suggest_int('min_samples_leaf', 5, 15,step = 1)
  max_features = trial.suggest_float('max_features',0.4,0.8)
  max_samples = trial.suggest_float('max_samples',0.4,0.8)
  class_0_weight = trial.suggest_float('class_0_weight',0.1,1)
  class_1_weight = trial.suggest_float('class_1_weight',0.1,1)
  threshold = trial.suggest_float('threshold',0.4,0.8)
  class_1_percent = trial.suggest_float('class_1_percent',0.01,0.5)
  random_state = trial.suggest_int('random_state', 1, 1000000)


  # создаем модель
  optuna_random_forest = RandomForestClassifier(
      n_estimators = n_estimators, 
      criterion = criterion,
      max_depth = max_depth,
      min_samples_split = min_samples_split,  
      min_samples_leaf = min_samples_leaf,
      max_features=max_features,
      max_samples=max_samples,
      class_weight={0:class_0_weight,1:class_1_weight},
      n_jobs=-1,
      random_state=42)

  # с помощью функции corr_transform_to_force получим
  # список не коррелируемых признаков
  list_ncorr_features = corr_transform_to_force(corr_matrix,threshold=threshold)[1]

  # сформируем данные для анализа сбалансированности обучающих данных
  X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
  y_train_pd = pd.read_csv('target/target_train.csv')

  # поготовим данные y_train_pd к работе с функцией class_1_percent_samples
  y_train_pd.set_index('id',drop=False,inplace=True)

  # подготовим данные для обучения модели
  # с помощью функции class_1_percent_samples зададим долю 
  # класса 1
  list_c1_percent_id = class_1_percent_samples(y_train_pd,class_1_percent,random_state=random_state)[:1000000]

  # подготовим данные для обучения
  X_train_balanced = X_train_pd.loc[list_c1_percent_id]
  y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']

  # освободим память от "тяжелых" и ненужных файлов
  del X_train_pd, y_train_pd
  gc.collect()

  # я не воспользовался параметром timeout метода optimize потому, что  
  # optimize отставливает поиск параметров, если время обучения 
  # превышает timeout. Мне нужно чтобы поиск параметров продолжился.
  try:
    # для модуля func_time_out упакуем обучение модели в функцию try_func
    def try_func():
            return optuna_random_forest.fit(X_train_balanced, y_train_balanced)
    # обучаем модель с ограничением по времени 10 минут (600 секунд)
    optuna_random_forest = func_timeout.func_timeout(600, try_func)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train_balanced, y_train_balanced
    gc.collect()

    # загружаем тестовые наборы
    # сформируем данные для анализа сбалансированности обучающих данных
    X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
    X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()[list_ncorr_features]
    y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
    y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()
    
    # делаем предсказание на обучающем и валидационном наборе
    #Считаем метрики для класса 1 добавляем их в список
    roc_train = metrics.roc_auc_score(y_train, optuna_random_forest.predict_proba(X_train)[:,1])
    roc_valid = metrics.roc_auc_score(y_valid, optuna_random_forest.predict_proba(X_valid)[:,1])
    f1_score = metrics.f1_score(y_valid, optuna_random_forest.predict(X_valid))
    recall_1 = metrics.recall_score(y_valid, optuna_random_forest.predict(X_valid),average=None,zero_division=0)[1]
    precision_1 = metrics.precision_score(y_valid, optuna_random_forest.predict(X_valid),average=None,zero_division=0)[1]

    # удаляем крупные файлы чтобы высвободить память 
    del X_train, X_valid, y_train, y_valid
    gc.collect()

  except func_timeout.FunctionTimedOut:
    # удаляем крупные файлы чтобы высвободить память 
    del X_train_balanced, y_train_balanced
    gc.collect()
    
    # фиксируем пустые значения метрик
    roc_train = 0
    roc_valid = 0
    f1_score = 0
    recall_1 = 0
    precision_1 = 0
    pass

  return roc_train, roc_valid, f1_score, recall_1, precision_1

In [1726]:
# cоздаем объект исследования
optuna_study_rf = optuna.create_study(study_name= 'RandomForestClassifier_'+feature_space+'_stat', 
                               directions=['maximize','maximize','maximize','maximize','maximize'], 
                               sampler=optuna.samplers.TPESampler(),
                               pruner='Hyperband',
                               storage='sqlite:///optuna_studies.db',
                               load_if_exists=True)
# на случай удаления 
# optuna.delete_study(study_name='RandomForestClassifier_'+feature_space+'_stat', storage='sqlite:///optuna_studies.db')

[I 2025-04-19 14:49:26,801] Using an existing study with name 'RandomForestClassifier_credit_stat' instead of creating a new one.


In [869]:
# ищем лучшую комбинацию гиперпараметров n_trials раз
optuna_study_rf.optimize(optuna_rf, n_trials=300)

[I 2025-04-18 01:08:06,323] Trial 0 finished with values: [0.9314152566424097, 0.6294144729497105, 0.06792058516196448, 0.0519376747902517, 0.09811320754716982] and parameters: {'n_estimators': 70, 'criterion': 'entropy', 'max_depth': 30, 'min_samples_split': 14, 'min_samples_leaf': 5, 'max_features': 0.5215310115960453, 'max_samples': 0.7535361830594106, 'class_0_weight': 0.4903457578664116, 'class_1_weight': 0.6629085115501296, 'threshold': 0.640921088070776, 'class_1_percent': 0.2091888359731302, 'random_state': 157337}.
[I 2025-04-18 01:08:11,166] Trial 1 finished with values: [0.7560488490343713, 0.6250371403269486, 0.08540323943321988, 0.7067518977227327, 0.0454475387935464] and parameters: {'n_estimators': 50, 'criterion': 'gini', 'max_depth': 28, 'min_samples_split': 12, 'min_samples_leaf': 9, 'max_features': 0.7394384195149929, 'max_samples': 0.4938427282168967, 'class_0_weight': 0.15768649305582758, 'class_1_weight': 0.2226596282657745, 'threshold': 0.4688938037441988, 'class

In [1727]:
# из полученного результат соврмируем Data Frame
optuna_study_rf_pd = optuna_study_rf.trials_dataframe().dropna()
# переименуем столбы
optuna_study_rf_pd.rename(columns={
    'values_0': 'roc_train',
    'values_1': 'roc_valid',
    'values_2': 'f1_score',
    'values_3': 'recall_1',
    'values_4': 'precision_1'
},inplace=True)
optuna_study_rf_pd.tail()

number  roc_train  roc_valid  f1_score  recall_1  precision_1  \
295     295   0.817860   0.637938  0.072022  0.965641     0.037406   
296     296   0.804512   0.634162  0.075310  0.925290     0.039252   
297     297   0.843911   0.640302  0.092472  0.636037     0.049861   
298     298   0.830217   0.644255  0.089860  0.749501     0.047795   
299     299   0.826527   0.639479  0.088260  0.737515     0.046939   

                datetime_start          datetime_complete  \
295 2025-04-18 02:02:13.706100 2025-04-18 02:02:26.630803   
296 2025-04-18 02:02:26.636596 2025-04-18 02:02:37.837456   
297 2025-04-18 02:02:37.842472 2025-04-18 02:02:50.031065   
298 2025-04-18 02:02:50.036664 2025-04-18 02:03:02.845527   
299 2025-04-18 02:03:02.850939 2025-04-18 02:03:12.970769   

                  duration  params_class_0_weight  ...  params_criterion  \
295 0 days 00:00:12.924703               0.115254  ...          log_loss   
296 0 days 00:00:11.200860               0.101710  ...          log_loss   
297 0 days 00:00:12.188593               0.118830  ...          log_loss   
298 0 days 00:00:12.808863               0.143946  ...          log_loss   
299 0 days 00:00:10.119830               0.139656  ...          log_loss   

     params_max_depth params_max_features  params_max_samples  \
295                25            0.799274            0.784989   
296                25            0.799881            0.786207   
297                26            0.791967            0.792243   
298                25            0.766221            0.677551   
299                27            0.750317            0.677581   

     params_min_samples_leaf  params_min_samples_split  params_n_estimators  \
295                       13                         8                  100   
296                       13                         8                  100   
297                       14                         5                  100   
298                       13                         8                  100   
299                       13                         8                   55   

     params_random_state  params_threshold     state  
295               594744          0.783274  COMPLETE  
296               589871          0.527634  COMPLETE  
297               546969          0.656674  COMPLETE  
298               593112          0.771082  COMPLETE  
299               625965          0.772454  COMPLETE  

[5 rows x 22 columns]

In [1728]:
# покаждем статистику обучения
print('Максимальное значение метрики ROC AUC на валидационном наборе:',round(optuna_study_rf_pd['roc_valid'].max(),3))
print('Среднее значение метрики ROC AUC на валидационном наборе:',round(optuna_study_rf_pd['roc_valid'].mean(),3))
print('Максимальное значение метрики f1_score на валидационном наборе:',round(optuna_study_rf_pd['f1_score'].max(),3))
print('Среднее значение метрики f1_score на валидационном наборе:',round(optuna_study_rf_pd['f1_score'].mean(),3))
print('Максимальное значение метрики recall_1 на валидационном наборе:',round(optuna_study_rf_pd['recall_1'].max(),3))
print('Среднее значение метрики recall_1 на валидационном наборе:',round(optuna_study_rf_pd['recall_1'].mean(),3))
print('Максимальное значение метрики precision_1 на валидационном наборе:',round(optuna_study_rf_pd['precision_1'].max(),3))
print('Среднее значение метрики precision_1 на валидационном наборе:',round(optuna_study_rf_pd['precision_1'].mean(),3))

Максимальное значение метрики ROC AUC на валидационном наборе: 0.646
Среднее значение метрики ROC AUC на валидационном наборе: 0.635
Максимальное значение метрики f1_score на валидационном наборе: 0.114
Среднее значение метрики f1_score на валидационном наборе: 0.083
Максимальное значение метрики recall_1 на валидационном наборе: 0.996
Среднее значение метрики recall_1 на валидационном наборе: 0.333
Максимальное значение метрики precision_1 на валидационном наборе: 1.0
Среднее значение метрики precision_1 на валидационном наборе: 0.074


In [1730]:
# Построим зависимость метрик качества модели от number

fig = px.scatter(
    data_frame=optuna_study_rf_pd[(optuna_study_rf_pd['roc_valid']>=0.999*optuna_study_rf_pd['roc_valid'].max())],
    x='number', #ось абсцисс
    y=['roc_valid','roc_train','precision_1','recall_1'], #ось ординат
)
fig.update_layout(
    title ={
        'text':'Зависимость качества модели от trials optuna', # Имя рабочей плоскости
        'font':{'size':35,'family':"Times New Roman"}, # размер и стиль написания имени рабочей плоскости
        'x':0.5, # Смешение имени по оси "x" на половину рабочей плоскости
        },
    height =800,# Высота рабочей плоскости
    width = 1350, # Ширина рабочей плоскости
    bargap=0.2, # Добавил расстояния между столбами гистограммы
    xaxis_title='trials optuna',
    yaxis_title='Величина параметра')
fig.update_xaxes(showspikes=True)
fig.update_yaxes(showspikes=True)

fig.show()

<span style="color:Blue">

Вывод:  

Их всех выбираем точку $number =163$.   
Не смотря на, то что в этой точке модель подает признаки переобучеености,  
в этой точке оптимальные значения метрик $recall_1$ и $precision_1$, а  
также относительно высокая метрика $ROC AUC$.   
Посмотрим каким значениям гиперпараметров соотвествует выбраннаяточка.

In [1731]:
# определим номер лучшге варианта
best_optuna_number = 163

# сформируем словарь лучших гипирпарметров RandomForestClassifier
best_param_rf = {
    'n_estimators' : int(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_n_estimators'].iloc[0]),
    'criterion': optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_criterion'].iloc[0],
    'max_depth' : int(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_max_depth'].iloc[0]),
    'min_samples_split': int(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_min_samples_split'].iloc[0]),
    'min_samples_leaf' : int(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_min_samples_leaf'].iloc[0]),
    'max_features': optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_max_features'].iloc[0],
    'max_samples' : optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_max_samples'].iloc[0],
    'class_weight' : {0:optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_class_0_weight'].iloc[0],
                      1:optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_class_1_weight'].iloc[0]}
    }

# определим перменные для лучших значений параметров
best_threshold = optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_threshold'].iloc[0]
best_class_1_percent = optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_class_1_percent'].iloc[0]
best_random_state = optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_random_state'].iloc[0]


# Выведем принятые наилучшие праметры
print('best n estimators:',best_param_rf['n_estimators'])
print('best criterion:',best_param_rf['criterion'])
print('best max depth:',best_param_rf['max_depth'])
print('best min samples split:',best_param_rf['min_samples_split'])
print('best min samples leaf:',best_param_rf['min_samples_leaf'])
print('best max features(%):',round(best_param_rf['max_features'],3))
print('best max samples(%):',round(best_param_rf['max_samples'],3))
print('best class 0 weight:',round(best_param_rf['class_weight'][0],3))
print('best class 1 weight:',round(best_param_rf['class_weight'][1],3))

print('best class 1 percent:',round(best_class_1_percent,3))
print('best threshold:',round(best_threshold,3))
print('best random state:', best_random_state)
print('time for best train:',round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['duration'].iloc[0].seconds/60),'minutes')

print()
print('ROC AUC на обучающем наборе:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['roc_train'].iloc[0],3))
print('ROC AUC на валидационном наборе:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['roc_valid'].iloc[0],3))
print('precision класса 1:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['precision_1'].iloc[0],3))
print('recall класса 1:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['recall_1'].iloc[0],3))

best n estimators: 100
best criterion: gini
best max depth: 30
best min samples split: 8
best min samples leaf: 15
best max features(%): 0.756
best max samples(%): 0.75
best class 0 weight: 0.172
best class 1 weight: 0.558
best class 1 percent: 0.229
best threshold: 0.779
best random state: 925697
time for best train: 0 minutes

ROC AUC на обучающем наборе: 0.871
ROC AUC на валидационном наборе: 0.646
precision класса 1: 0.068
recall класса 1: 0.339


##### <span style="color:MediumSlateBlue">Обучение модели с лучшими параметрами</span>

In [1732]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'credit'
count_features = dict_spaces[feature_space]

# для работы функции corr_transform_to_force
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()

# с помощью функции corr_transform_to_force получим
# список не коррелируемых признаков
list_ncorr_features = corr_transform_to_force(corr_matrix,threshold=best_threshold)[1]

# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
y_train_pd = pd.read_csv('target/target_train.csv')

# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)

# подготовим данные для обучения модели
# с помощью функции class_1_percent_samples зададим долю 
# класса 1
list_c1_percent_id = class_1_percent_samples(y_train_pd,best_class_1_percent,random_state=best_random_state)[:1000000]

# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']

# освободим память от "тяжелых" и ненужных файлов
del X_train_pd, y_train_pd
gc.collect()


# обучаем модель RandomForestClassifier с наилучшеми параметрами
random_forest = RandomForestClassifier(
        **best_param_rf,
        n_jobs=-1,
        random_state=42)
random_forest.fit(X_train_balanced, y_train_balanced)

# удаляем крупные файлы чтобы высвободить память 
del X_train_balanced, y_train_balanced
gc.collect()

# загружаем тестовые наборы
# сформируем данные для анализа сбалансированности обучающих данных
X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()[list_ncorr_features]
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_rf_pred_proba = random_forest.predict_proba(X_train)[:,1]
y_valid_rf_pred_proba = random_forest.predict_proba(X_valid)[:,1]

# Делаем предсказание для валидационной выборки
y_valid_rf_pred = random_forest.predict(X_valid)

# удаляем крупные файлы чтобы высвободить память 
del X_train, X_valid
gc.collect()

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_rf_pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_rf_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_rf_pred,zero_division=0))

# time: 5m 30s

ROC AUC на обучающем наборе 0.871
ROC AUC на валидационном наборе 0.646
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.97      0.83      0.89     68747
           1       0.07      0.34      0.11      2503

    accuracy                           0.81     71250
   macro avg       0.52      0.58      0.50     71250
weighted avg       0.94      0.81      0.87     71250



#### <span style="color:MediumBlue">Построение модели Gradient Boosting Classifier</span>

##### <span style="color:MediumSlateBlue">Формирование данных для обучения</span>

Анализ исходных данных, в частности target, показал что представленные данные   
имееют перекос: 96% клиентов у которых не случился дефолт (flag = 0),    
против 4 % - для которых произошел дефолт (flag = 1).  
С помощью функции class_1_percent_samples, сформируем сбаланисрованную выборку  
для обучения моделей.
За основу сбалансировных данных возьмем данные клиентов с дефолтом  
и к ним будем добирать необходимое количество клиентов до сбалансированности. 


Функция class_1_percent_samples принемает две переменные:
- target_data - массив с id и целевой переменной
- class_1_percent - процент класса 1 в результирующем массиве

In [886]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'credit'
count_features = dict_spaces[feature_space]

In [887]:
# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

In [888]:
# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)
y_train_pd.head(4)

id  flag
id                    
1825800  1825800     0
2166483  2166483     0
2534345  2534345     0
1803283  1803283     0

In [889]:
# взглянем на сблансиорованность данных в y_train
y_train_pd['flag'].value_counts(normalize=True)

flag
0    0.964242
1    0.035758
Name: proportion, dtype: float64

In [890]:
# сбалансируем данные в y_train_pd
list_c1_percent_id = class_1_percent_samples(y_train_pd,0.5)
# list_c1_percent_features - список 'id' из y_train_pd соотвествующих  
# заданному проценту класса 1
len(list_c1_percent_id)

45860

In [891]:
# проверим сбалансированность полученного y_train
y_train_pd.loc[list_c1_percent_id]['flag'].value_counts(normalize=True)

flag
1    0.5
0    0.5
Name: proportion, dtype: float64

В отличие от данных в *transform_data_torow*, где модели показываеются последние N  
операций клиента, в данные в *transform_data_stat* сфомированы из различных статистических   
характеристик ряда определяющего клиентскую историю в банке. 

Соотвественно, если в данных *transform_data_torow* была сильная корреляция между признаками,  
то я не смог бы ее убрать, иначе потярется смысл "показать последовательный ряд в историии клиента".  
Признаки в *transform_data_stat* не имеют такой особенности. Поэтому, необходимо проанализировать  
данные в *transform_data_stat* и, в случае сильной коррреляции признаков, устранить ее.

In [892]:
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()
corr_matrix.shape

(69, 69)

In [893]:
# с помощью функции corr_transrom_to_power получим
# силу корреляции матрицы и список не коррелируемых признаков

# для начального анализа зададим порог силы корреляции, при котором признаки 
# будут отнесены к "сильно скоррелированными" равным 0.6
ncorr_matrix,list_ncorr_features,corr_power =corr_transform_to_force(corr_matrix,threshold=0.6)

# Выведем результаты преобразования
print('Исходное количество признаков: ', corr_matrix.shape[0])
print('Количество не коррелируемых признаков: ', len(list_ncorr_features))
# сила корреляции признаков
print('Отношение коррелируемых исходному количеству признаков (сила корреляции): ',corr_power)

Исходное количество признаков:  69
Количество не коррелируемых признаков:  24
Отношение коррелируемых исходному количеству признаков (сила корреляции):  0.652


In [894]:
# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']
# сформируем данные для проверики модели
# сформируем данные для анализа сбалансированности обучающих данных
X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()
y_train = pd.read_csv('target/target_train.csv')['flag']
X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()
y_valid = pd.read_csv('target/target_valid.csv')['flag']

In [895]:
# посмотрим на структуру данных в X_train_balanced
X_train_balanced.head(4)

f1    f2      f3     f4     f5      f6      f7   f8     f9  f10  \
id                                                                           
2335465  17.0  19.0  10.824  0.000  0.000  18.464  10.824  0.0  7.246  0.0   
390270    6.0  17.0  10.167  8.165  8.165  18.331  10.167  0.0  5.520  2.0   
2494034  14.0  16.0  10.643  8.958  8.958  18.276  10.643  0.0  5.702  3.0   
2018674  15.0  19.0  10.333  0.000  0.000  18.022  10.333  0.0  6.529  0.0   

         ...    f60  f61  f62  f63  f64   f65  f66   f67     f68  f69  
id       ...                                                           
2335465  ...  3.291  1.0  2.0  3.0  5.4  13.0  2.0  0.29  11.507  7.0  
390270   ...  1.700  0.0  1.0  2.5  4.0   4.0  4.0  0.50   3.467  2.0  
2494034  ...  3.731  0.0  4.0  4.0  4.3  13.0  4.0  0.64  14.989  6.5  
2018674  ...  3.197  0.0  2.0  2.0  2.0  11.0  2.0  0.67  10.952  5.5  

[4 rows x 69 columns]

In [896]:
# посмотрим на структуру данных в y_train_balanced
y_train_balanced.head(4)

id
2335465    1
390270     1
2494034    1
2018674    1
Name: flag, dtype: int64

In [897]:
# проверим что выборки действительно совпадают по id
X_train_balanced.index.to_list() == y_train_balanced.index.to_list()

True

##### <span style="color:MediumSlateBlue">Baseline обучение модели Hist Gradient Boosting Classifier</span>

In [898]:
# обучаем модель Gradient Boosting Classifier
gradient_boosting = HistGradientBoostingClassifier(random_state=42)
gradient_boosting.fit(X_train_balanced[list_ncorr_features],y_train_balanced)

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_rf__pred_proba = gradient_boosting.predict_proba(X_train[list_ncorr_features])[:,1]
y_valid_rf_pred_proba = gradient_boosting.predict_proba(X_valid[list_ncorr_features])[:,1]

# Делаем предсказание для валидационной выборки
y_valid_rf_pred = gradient_boosting.predict(X_valid[list_ncorr_features])

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_rf__pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_rf_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_rf_pred))

# time: 30s

ROC AUC на обучающем наборе 0.67
ROC AUC на валидационном наборе 0.643
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.98      0.58      0.73     68747
           1       0.05      0.62      0.09      2503

    accuracy                           0.58     71250
   macro avg       0.51      0.60      0.41     71250
weighted avg       0.94      0.58      0.71     71250



##### <span style="color:MediumSlateBlue">Подбор гиперпараметров модели</span>

In [1733]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'credit'
count_features = dict_spaces[feature_space]

# для работы функции corr_transform_to_force
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()

# настроим оптимизацию гипер параметров
def optuna_hgbc(trial):
  # задаем пространства поиска гиперпараметров
  learning_rate = trial.suggest_float('learning_rate',0.01,0.1)
  max_iter = trial.suggest_int('max_iter', 150, 250,step = 1)
  max_leaf_nodes = trial.suggest_int('max_leaf_nodes', 2, 60,step = 1)
  max_depth = trial.suggest_int('max_depth', 1, 10,step = 1)
  min_samples_leaf = trial.suggest_int('min_samples_leaf', 1, 60,step = 1)
  max_features = trial.suggest_float('max_features',0.6,1)
  l2_regularization = trial.suggest_float('l2_regularization',0.01,1)
  class_0_weight = trial.suggest_float('class_0_weight',0.01,1)
  class_1_weight = trial.suggest_float('class_1_weight',0.5,1)
  threshold = trial.suggest_float('threshold',0.7,1)
  class_1_percent = trial.suggest_float('class_1_percent',0.01,0.25)
  random_state = trial.suggest_int('random_state', 1, 1000000)

  # создаем модель
  optuna_gradient_boosting = HistGradientBoostingClassifier(
      learning_rate= learning_rate,
      max_iter = max_iter,
      max_leaf_nodes =max_leaf_nodes,
      max_depth = max_depth,
      min_samples_leaf = min_samples_leaf,
      max_features=max_features,
      l2_regularization = l2_regularization,
      class_weight={0:class_0_weight,1:class_1_weight},
      random_state=42)

  # с помощью функции corr_transform_to_force получим
  # список не коррелируемых признаков
  list_ncorr_features = corr_transform_to_force(corr_matrix,threshold=threshold)[1]

  # сформируем данные для анализа сбалансированности обучающих данных
  X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
  y_train_pd = pd.read_csv('target/target_train.csv')

  # поготовим данные y_train_pd к работе с функцией class_1_percent_samples
  y_train_pd.set_index('id',drop=False,inplace=True)

  # подготовим данные для обучения модели
  # с помощью функции class_1_percent_samples зададим долю 
  # класса 1
  list_c1_percent_id = class_1_percent_samples(y_train_pd,class_1_percent,random_state=random_state)[:1000000]

  # подготовим данные для обучения
  X_train_balanced = X_train_pd.loc[list_c1_percent_id]
  y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']

  # освободим память от "тяжелых" и ненужных файлов
  del X_train_pd, y_train_pd
  gc.collect()

  # я не воспользовался параметром timeout метода optimize потому, что  
  # optimize отставливает поиск параметров, если время обучения 
  # превышает timeout. Мне нужно чтобы поиск параметров продолжился.
  try:
    # для модуля func_time_out упакуем обучение модели в функцию try_func
    def try_func():
            return optuna_gradient_boosting.fit(X_train_balanced,y_train_balanced)
    # обучаем модель с ограничением по времени 10 минут (600 секунд)
    optuna_gradient_boosting = func_timeout.func_timeout(600, try_func)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train_balanced, y_train_balanced
    gc.collect()

        # загружаем тестовые наборы
    # сформируем данные для анализа сбалансированности обучающих данных
    X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
    X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()[list_ncorr_features]
    y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
    y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()
    
    # делаем предсказание на обучающем и валидационном наборе и считаем метрики
    roc_train = metrics.roc_auc_score(y_train, optuna_gradient_boosting.predict_proba(X_train)[:,1])
    roc_valid = metrics.roc_auc_score(y_valid, optuna_gradient_boosting.predict_proba(X_valid)[:,1])
    f1_score = metrics.f1_score(y_valid, optuna_gradient_boosting.predict(X_valid))
    recall_1 = metrics.recall_score(y_valid, optuna_gradient_boosting.predict(X_valid),average=None,zero_division=0)[1]
    precision_1 = metrics.precision_score(y_valid, optuna_gradient_boosting.predict(X_valid),average=None,zero_division=0)[1]


    # удаляем крупные файлы чтобы высвободить память 
    del X_train, X_valid, y_train, y_valid
    gc.collect()

  except func_timeout.FunctionTimedOut:
    # удаляем крупные файлы чтобы высвободить память 
    del X_train_balanced, y_train_balanced
    gc.collect()
    
    # фиксируем пустые значения метрик
    roc_train = 0
    roc_valid = 0
    f1_score = 0
    recall_1 = 0
    precision_1 = 0
    pass

  return roc_train, roc_valid, f1_score, recall_1, precision_1

In [1734]:
# cоздаем объект исследования
# чтобы модель не переобучалась минимизируем roc_train 
# и максимизируем roc_valid
optuna_study_hgbc = optuna.create_study(study_name='HistGradientBoostingClassifier_'+feature_space+'_stat', 
                               directions=['maximize','maximize','maximize','maximize','maximize'], 
                               sampler=optuna.samplers.TPESampler(),
                               pruner='Hyperband',
                               storage='sqlite:///optuna_studies.db',
                               load_if_exists=True)

# ну случай удаления обучения
# optuna.delete_study(study_name='HistGradientBoostingClassifier'+feature_space+'_stat', storage='sqlite:///optuna_studies.db')

[I 2025-04-19 14:51:06,598] Using an existing study with name 'HistGradientBoostingClassifier_credit_stat' instead of creating a new one.


In [901]:
# ищем лучшую комбинацию гиперпараметров n_trials раз
optuna_study_hgbc.optimize(optuna_hgbc, n_trials=300)

[I 2025-04-18 02:03:51,727] Trial 0 finished with values: [0.6990315647940875, 0.6498849060299096, 0.10671044531089678, 0.4155013983220136, 0.06121608099358408] and parameters: {'learning_rate': 0.049975863669941153, 'max_iter': 243, 'max_leaf_nodes': 47, 'max_depth': 9, 'min_samples_leaf': 37, 'max_features': 0.7033708278249735, 'l2_regularization': 0.8449107992692806, 'class_0_weight': 0.25748697738469434, 'class_1_weight': 0.908492280998801, 'threshold': 0.7352194552976525, 'class_1_percent': 0.1870797963953913, 'random_state': 475762}.
[I 2025-04-18 02:03:56,339] Trial 1 finished with values: [0.6164324906431603, 0.6151620397443442, 0.06787520507640367, 1.0, 0.03512982456140351] and parameters: {'learning_rate': 0.06538818221756117, 'max_iter': 194, 'max_leaf_nodes': 10, 'max_depth': 1, 'min_samples_leaf': 25, 'max_features': 0.7215388102720793, 'l2_regularization': 0.583724080513221, 'class_0_weight': 0.07865896365229534, 'class_1_weight': 0.8863363004337499, 'threshold': 0.748255

In [1735]:
# из полученного результат соврмируем Data Frame
optuna_study_hgbc_pd = optuna_study_hgbc.trials_dataframe()
# переименуем столбы
optuna_study_hgbc_pd.rename(columns={
    'values_0': 'roc_train',
    'values_1': 'roc_valid',
    'values_2': 'f1_score',
    'values_3': 'recall_1',
    'values_4': 'precision_1'
},inplace=True)
optuna_study_hgbc_pd.tail(5)

number  roc_train  roc_valid  f1_score  recall_1  precision_1  \
295     295   0.715249   0.657286  0.111407  0.359569     0.065915   
296     296   0.703072   0.657680  0.097883  0.640032     0.052994   
297     297   0.712261   0.655590  0.112924  0.389932     0.066022   
298     298   0.710171   0.659791  0.113407  0.436276     0.065175   
299     299   0.681233   0.653112  0.112379  0.417099     0.064937   

                datetime_start          datetime_complete  \
295 2025-04-18 02:49:42.716698 2025-04-18 02:49:57.127694   
296 2025-04-18 02:49:57.133571 2025-04-18 02:50:10.575784   
297 2025-04-18 02:50:10.581455 2025-04-18 02:50:24.754748   
298 2025-04-18 02:50:24.760420 2025-04-18 02:50:38.384108   
299 2025-04-18 02:50:38.390073 2025-04-18 02:50:53.524725   

                  duration  params_class_0_weight  ...  \
295 0 days 00:00:14.410996               0.203641  ...   
296 0 days 00:00:13.442213               0.189967  ...   
297 0 days 00:00:14.173293               0.219620  ...   
298 0 days 00:00:13.623688               0.184738  ...   
299 0 days 00:00:15.134652               0.181292  ...   

     params_l2_regularization  params_learning_rate  params_max_depth  \
295                  0.307321              0.043508                 9   
296                  0.266184              0.046384                 8   
297                  0.134490              0.041563                 9   
298                  0.346271              0.044733                 9   
299                  0.351178              0.014800                 8   

     params_max_features  params_max_iter  params_max_leaf_nodes  \
295             0.628767              247                     56   
296             0.609830              235                     42   
297             0.623501              242                     58   
298             0.600494              245                     59   
299             0.743864              167                     59   

     params_min_samples_leaf  params_random_state  params_threshold     state  
295                        1               644871          0.983588  COMPLETE  
296                       16               934621          0.977115  COMPLETE  
297                        6               952527          0.999998  COMPLETE  
298                        9               670200          0.991068  COMPLETE  
299                       19               830775          0.974670  COMPLETE  

[5 rows x 22 columns]

In [1736]:
# покаждем статистику обучения
print('Максимальное значение метрики ROC AUC на валидационном наборе:',round(optuna_study_hgbc_pd['roc_valid'].max(),3))
print('Среднее значение метрики ROC AUC на валидационном наборе:',round(optuna_study_hgbc_pd['roc_valid'].mean(),3))
print('Максимальное значение метрики f1_score на валидационном наборе:',round(optuna_study_hgbc_pd['f1_score'].max(),3))
print('Среднее значение метрики f1_score на валидационном наборе:',round(optuna_study_hgbc_pd['f1_score'].mean(),3))
print('Максимальное значение метрики recall_1 на валидационном наборе:',round(optuna_study_hgbc_pd['recall_1'].max(),3))
print('Среднее значение метрики recall_1 на валидационном наборе:',round(optuna_study_hgbc_pd['recall_1'].mean(),3))
print('Максимальное значение метрики precision_1 на валидационном наборе:',round(optuna_study_hgbc_pd['precision_1'].max(),3))
print('Среднее значение метрики precision_1 на валидационном наборе:',round(optuna_study_hgbc_pd['precision_1'].mean(),3))

Максимальное значение метрики ROC AUC на валидационном наборе: 0.661
Среднее значение метрики ROC AUC на валидационном наборе: 0.654
Максимальное значение метрики f1_score на валидационном наборе: 0.118
Среднее значение метрики f1_score на валидационном наборе: 0.078
Максимальное значение метрики recall_1 на валидационном наборе: 1.0
Среднее значение метрики recall_1 на валидационном наборе: 0.371
Максимальное значение метрики precision_1 на валидационном наборе: 0.212
Среднее значение метрики precision_1 на валидационном наборе: 0.07


In [1740]:
# Построим зависимость метрик качества модели от number

fig = px.scatter(
    data_frame=optuna_study_hgbc_pd[(optuna_study_hgbc_pd['roc_valid']>0.9999*optuna_study_hgbc_pd['roc_valid'].max())],
    x='number', #ось абсцисс
    y=['roc_train','roc_valid','recall_1','precision_1','f1_score'], #ось ординат
)
fig.update_layout(
    title ={
        'text':'Зависимость качества модели от trials optuna', # Имя рабочей плоскости
        'font':{'size':35,'family':"Times New Roman"}, # размер и стиль написания имени рабочей плоскости
        'x':0.5, # Смешение имени по оси "x" на половину рабочей плоскости
        },
    height =800,# Высота рабочей плоскости
    width = 1350, # Ширина рабочей плоскости
    bargap=0.2, # Добавил расстояния между столбами гистограммы
    xaxis_title='trials optuna',
    yaxis_title='Величина параметра')
fig.update_xaxes(showspikes=True)
fig.update_yaxes(showspikes=True)

fig.show()

<span style="color:Blue">

Вывод:  

Их всех выбираем точку $number =176$.   
В этой точке оптимальные значения метрик $recall_1$ и $precision_1$, а  
также относительно высокая метрика $ROC AUC$.   
Посмотрим каким значениям гиперпараметров соотвествует выбранная точка.

In [1741]:
# определим номер лучшге варианта
best_optuna_number = 176

# сформируем словарь лучших гипирпарметров HistGradientBoostingClassifier
best_param_hgbc = {
    'learning_rate' : optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_learning_rate'].iloc[0],
    'max_iter' : optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_max_iter'].iloc[0],
    'max_leaf_nodes' : optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_max_leaf_nodes'].iloc[0],
    'max_depth' : optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_max_depth'].iloc[0],
    'min_samples_leaf' : optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_min_samples_leaf'].iloc[0],
    'max_features' : optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_max_features'].iloc[0],
    'l2_regularization' : optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_l2_regularization'].iloc[0],
    'class_weight' : {0: optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_class_0_weight'].iloc[0],
                      1: optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_class_1_weight'].iloc[0],}
    }

# определим перменные для лучших значений параметров
best_threshold = optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_threshold'].iloc[0]
best_class_1_percent = optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_class_1_percent'].iloc[0]
best_random_state = optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_random_state'].iloc[0]


# Выведем принятые наилучшие параметры
print('best learning rate:',round(best_param_hgbc['learning_rate'],3))
print('best max iter:',best_param_hgbc['max_iter'])
print('best max leaf nodes:',best_param_hgbc['max_leaf_nodes'])
print('best max depth:',best_param_hgbc['max_depth'])
print('best min samples leaf:',best_param_hgbc['min_samples_leaf'])
print('best max features:',round(best_param_hgbc['max_features'],3))
print('best l2 regularization:',round(best_param_hgbc['l2_regularization'],3))
print('best class 0 weight:',round(best_param_hgbc['class_weight'][0],3))
print('best class 1 weight:',round(best_param_hgbc['class_weight'][1],3))

print('best class 1 percent:',round(best_class_1_percent,3))
print('best threshold:',round(best_threshold,3))
print('time for best train:',round(optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['duration'].iloc[0].seconds/60),'minutes')

print()
print('ROC AUC на обучающем наборе:', round(optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['roc_train'].iloc[0],3))
print('ROC AUC на валидационном наборе:', round(optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['roc_valid'].iloc[0],3))
print('precision класса 1:', round(optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['precision_1'].iloc[0],3))
print('recall класса 1:', round(optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['recall_1'].iloc[0],3))

best learning rate: 0.057
best max iter: 155
best max leaf nodes: 57
best max depth: 7
best min samples leaf: 60
best max features: 0.894
best l2 regularization: 0.804
best class 0 weight: 0.074
best class 1 weight: 0.653
best class 1 percent: 0.014
best threshold: 0.866
time for best train: 0 minutes

ROC AUC на обучающем наборе: 0.723
ROC AUC на валидационном наборе: 0.661
precision класса 1: 0.175
recall класса 1: 0.007


##### <span style="color:MediumSlateBlue">Обучение модели с лучшими параметрами</span>

In [1742]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'credit'
count_features = dict_spaces[feature_space]

# для работы функции corr_transform_to_force
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()

# с помощью функции corr_transform_to_force получим
# список не коррелируемых признаков
list_ncorr_features = corr_transform_to_force(corr_matrix,threshold=best_threshold)[1]

# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
y_train_pd = pd.read_csv('target/target_train.csv')

# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)

# подготовим данные для обучения модели
# с помощью функции class_1_percent_samples зададим долю 
# класса 1
list_c1_percent_id = class_1_percent_samples(y_train_pd,best_class_1_percent,random_state=best_random_state)[:1000000]

# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']

# освободим память от "тяжелых" и ненужных файлов
del X_train_pd, y_train_pd
gc.collect()

# обучаем модель HistGradientBoostingClassifier с наилучшеми параметрами
gradient_boosting = HistGradientBoostingClassifier(
        **best_param_hgbc,
        random_state=42)
gradient_boosting.fit(X_train_balanced,y_train_balanced)

# удаляем крупные файлы чтобы высвободить память 
del X_train_balanced, y_train_balanced
gc.collect()

# сформируем данные для анализа сбалансированности обучающих данных
X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()[list_ncorr_features]
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

# делаем предсказание на обучающем и валидационном наборе и считаем метрики
y_train_gb_pred_proba = gradient_boosting.predict_proba(X_train)[:,1]
y_valid_gb_pred_proba = gradient_boosting.predict_proba(X_valid)[:,1]
y_valid_gb_pred = gradient_boosting.predict(X_valid)

# удаляем крупные файлы чтобы высвободить память 
del X_train, X_valid
gc.collect()

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_gb_pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_gb_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_gb_pred,zero_division=0))

# time: 1m 40s

ROC AUC на обучающем наборе 0.722
ROC AUC на валидационном наборе 0.66
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.97      1.00      0.98     68747
           1       0.17      0.01      0.01      2503

    accuracy                           0.96     71250
   macro avg       0.57      0.50      0.50     71250
weighted avg       0.94      0.96      0.95     71250



### <span style="color:RoyalBlue">Построение модели на сбалансированных данных подпрострнства relative stat</span>

#### <span style="color:MediumBlue">Построение модели Logistic Regression</span>

##### <span style="color:MediumSlateBlue">Формирование данных для обучения</span>

Анализ исходных данных, в частности target, показал что представленные данные   
имееют перекос: 96% клиентов у которых не случился дефолт (flag = 0),    
против 4 % - для которых произошел дефолт (flag = 1).  
С помощью функции class_1_percent_samples, сформируем сбаланисрованную выборку  
для обучения моделей.
За основу сбалансировных данных возьмем данные клиентов с дефолтом  
и к ним будем добирать необходимое количество клиентов до сбалансированности. 


Функция class_1_percent_samples принемает две переменные:
- target_data - массив с id и целевой переменной
- class_1_percent - процент класса 1 в результирующем массиве

In [920]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'relative'
count_features = dict_spaces[feature_space]

In [921]:
# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

In [922]:
# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)
y_train_pd.head(4)

id  flag
id                    
1825800  1825800     0
2166483  2166483     0
2534345  2534345     0
1803283  1803283     0

In [923]:
# взглянем на сблансиорованность данных в y_train
y_train_pd['flag'].value_counts(normalize=True)

flag
0    0.964242
1    0.035758
Name: proportion, dtype: float64

In [924]:
# сбалансируем данные в y_train_pd
list_c1_percent_id = class_1_percent_samples(y_train_pd,0.5)
# list_c1_percent_features - список 'id' из y_train_pd соотвествующих  
# заданному проценту класса 1
len(list_c1_percent_id)

45860

In [925]:
# проверим сбалансированность полученного y_train
y_train_pd.loc[list_c1_percent_id]['flag'].value_counts(normalize=True)

flag
1    0.5
0    0.5
Name: proportion, dtype: float64

В отличие от данных в *transform_data_torow*, где модели показываеются последние N  
операций клиента, в данные в *transform_data_stat* сфомированы из различных статистических   
характеристик ряда определяющего клиентскую историю в банке. 

Соотвественно, если в данных *transform_data_torow* была сильная корреляция между признаками,  
то я не смог бы ее убрать, иначе потярется смысл "показать последовательный ряд в историии клиента".  
Признаки в *transform_data_stat* не имеют такой особенности. Поэтому, необходимо проанализировать  
данные в *transform_data_stat* и, в случае сильной коррреляции признаков, устранить ее.

In [926]:
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()
corr_matrix.shape

(103, 103)

In [927]:
# с помощью функции corr_transrom_to_power получим
# силу корреляции матрицы и список не коррелируемых признаков

# для начального анализа зададим порог силы корреляции, при котором признаки 
# будут отнесены к "сильно скоррелированными" равным 0.6
ncorr_matrix,list_ncorr_features,corr_power =corr_transform_to_force(corr_matrix,threshold=0.6)

# Выведем результаты преобразования
print('Исходное количество признаков: ', corr_matrix.shape[0])
print('Количество не коррелируемых признаков: ', len(list_ncorr_features))
# сила корреляции признаков
print('Отношение коррелируемых исходному количеству признаков (сила корреляции): ',corr_power)

Исходное количество признаков:  103
Количество не коррелируемых признаков:  27
Отношение коррелируемых исходному количеству признаков (сила корреляции):  0.738


In [928]:
# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']
# сформируем данные для проверики модели
# сформируем данные для анализа сбалансированности обучающих данных
X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()
y_train = pd.read_csv('target/target_train.csv')['flag']
X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()
y_valid = pd.read_csv('target/target_valid.csv')['flag']

In [929]:
# посмотрим на структуру данных в X_train_balanced
X_train_balanced.head(4)

f1    f2      f3      f4      f5      f6      f7   f8     f9  f10  \
id                                                                             
2335465  17.0  15.0  14.235  12.550  12.550  15.938  14.235  0.0  4.180  1.0   
390270    6.0  16.0  12.333   0.000   0.000  15.784  12.333  0.0  5.793  0.0   
2494034  14.0  13.0  12.500  11.422  11.422  15.822  12.500  0.0  4.355  3.0   
2018674  15.0   7.0  14.933  14.748  14.748  15.902  14.933  0.0  2.112  9.0   

         ...   f94  f95  f96  f97  f98  f99  f100  f101   f102  f103  
id       ...                                                          
2335465  ...  0.00  1.0  1.0  1.0  1.0  1.0   1.0  1.00  0.000   1.0  
390270   ...  0.00  1.0  1.0  1.0  1.0  1.0   1.0  1.00  0.000   1.0  
2494034  ...  0.35  0.0  1.0  1.0  1.0  1.0   1.0  0.86  0.132   0.5  
2018674  ...  0.34  0.0  1.0  1.0  1.0  1.0   1.0  0.87  0.124   0.5  

[4 rows x 103 columns]

In [930]:
# посмотрим на структуру данных в y_train_balanced
y_train_balanced.head(4)

id
2335465    1
390270     1
2494034    1
2018674    1
Name: flag, dtype: int64

In [931]:
# проверим что выборки действительно совпадают по id
X_train_balanced.index.to_list() == y_train_balanced.index.to_list()

True

##### <span style="color:MediumSlateBlue">Baseline обучение модели LogisticRegression</span>

In [932]:
# обучаем модель логистической регрессии
logistic_regression = linear_model.LogisticRegression(random_state=42, max_iter=10000)
logistic_regression.fit(X_train_balanced[list_ncorr_features],y_train_balanced)

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_LR_pred_proba = logistic_regression.predict_proba(X_train[list_ncorr_features])[:,1]
y_valid_LR_pred_proba = logistic_regression.predict_proba(X_valid[list_ncorr_features])[:,1]

# Делаем предсказание для валидационной выборки
y_valid_LR_pred = logistic_regression.predict(X_valid[list_ncorr_features])

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_LR_pred_proba),3))
print('ROC AUC на тестовом наборе', round(metrics.roc_auc_score(y_valid, y_valid_LR_pred_proba),3))

print('Основные метрики на тестовом наборе:')
print(metrics.classification_report(y_valid,y_valid_LR_pred))

# time: 3m 5s

ROC AUC на обучающем наборе 0.602
ROC AUC на тестовом наборе 0.611
Основные метрики на тестовом наборе:
              precision    recall  f1-score   support

           0       0.97      0.64      0.77     68747
           1       0.05      0.51      0.09      2503

    accuracy                           0.63     71250
   macro avg       0.51      0.57      0.43     71250
weighted avg       0.94      0.63      0.75     71250



##### <span style="color:MediumSlateBlue">Анализ влияния scaler преобразования на качество и скорость схождения модели</span>

In [933]:
# формируем список из необходимых scaler
scalers = [MinMaxScaler(),RobustScaler() ,StandardScaler()]

# сформируем списко для заполнения данными результатов анализа
scalers_data = []

# установим ограничение на время обучения модели в 600 секунд (10 минут)
time_out = 600

for scaler in scalers:
        # для того чтобы следить за выполнением цикла введем индикатор
        print('current scaler: ', scaler)

         # сформируем список для заполнения данными текушего scaler
        current_scaler_data = [scaler]
        
        # выполним scaler преобразование
        X_train_s_balanced = scaler.fit_transform(X_train_balanced[list_ncorr_features])
        X_train_s = scaler.transform(X_train[list_ncorr_features])
        X_valid_s = scaler.transform(X_valid[list_ncorr_features])

        try:
                # для модуля func_time_out упакуем обучение модели в функцию try_func
                def try_func():
                        logistic_regression = linear_model.LogisticRegression(random_state=42, max_iter=10000)
                        return logistic_regression.fit(X_train_s_balanced,y_train_balanced)
                    
                # фиксируем время начала
                start_time = time.time()
                
                # запускаем обучение модели с ограничением по времени
                logistic_regression = func_timeout.func_timeout(time_out, try_func)
                
                # фиксируем время окончания обучения
                end_time = time.time()
                
                # запишем время обучения модели
                current_scaler_data.append(round(end_time-start_time))

                # Делаем предсказание для обучающей и валидационной выборки
                y_valid_lr_pred = logistic_regression.predict(X_valid_s)
                
                # для метрик ROC AUC делаем предсказание модели для обучающей и валидационной выборки  
                # в виде вероятности принадлежности к классу 1 
                y_train_lr_pred_proba = logistic_regression.predict_proba(X_train_s)[:,1]
                y_valid_lr_pred_proba = logistic_regression.predict_proba(X_valid_s)[:,1]

                #Считаем метрики ROC AUC yна обуающем и валидационном наборе и добавляем их в спискок
                current_scaler_data.append(round(metrics.roc_auc_score(y_train, y_train_lr_pred_proba),3))
                current_scaler_data.append(round(metrics.roc_auc_score(y_valid, y_valid_lr_pred_proba),3))

                #Считаем метрики для класса 0 на валидационном наборе и добавляем их в список
                current_scaler_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))
                current_scaler_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))


                #Считаем метрики для класса 1 на валидационном набопе и добавляем их в список
                current_scaler_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))
                current_scaler_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))

                # добавляем полученные данные в список scalers_data
                scalers_data.append(current_scaler_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                scaler_pd =pd.DataFrame(
                        columns=['scaler','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = scalers_data)
                # сохраняем dataframe
                scaler_pd.to_csv('data_recovery/scaler_pd.csv',index=False)
               
                # очистим output от прошедшей итерации
                clear_output()

        except func_timeout.FunctionTimedOut:
                # если время обучения привышает лимит
                # запишем в current_scaler_data соотвествующую данные
                current_scaler_data = [scaler,'>30m',0,0,0,0,0,0]
                # добавляем полученные данные в список scalers_data
                scalers_data.append(current_scaler_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                scaler_pd =pd.DataFrame(
                        columns=['scaler','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = scalers_data)
                # сохраняем dataframe
                scaler_pd.to_csv('data_recovery/scaler_pd.csv',index=False)
                
                # очистим output от прошедшей итерации
                clear_output()
                # переходим к следующему scaler
                pass
# очистим output
clear_output()

# сформируем данные соотвествующие лучщему ROC AUC на валидацинном наборе
best_roc_valid_data = scaler_pd[scaler_pd['roc_valid']==scaler_pd['roc_valid'].max()]

# выведем лучший результат на валидационном наборе
print('result:')
print('best scaler on valid:',best_roc_valid_data.iloc[0]['scaler'])
print('ROC AUC on train:', best_roc_valid_data.iloc[0]['roc_train'])
print('ROC AUC on valid:', best_roc_valid_data.iloc[0]['roc_valid'])
print('Time fit for best scaler:', best_roc_valid_data.iloc[0]['time_fit'],' seconds')

# выведем полученный dataframe
scaler_pd

# time: 

result:
best scaler on valid: MinMaxScaler()
ROC AUC on train: 0.602
ROC AUC on valid: 0.611
Time fit for best scaler: 0  seconds


scaler  time_fit  roc_train  roc_valid  recall_0  precision_0  \
0    MinMaxScaler()         0      0.602      0.611     0.642        0.973   
1    RobustScaler()         0      0.602      0.611     0.643        0.973   
2  StandardScaler()         0      0.602      0.611     0.643        0.973   

   recall_1  precision_1  
0     0.512        0.049  
1     0.505        0.049  
2     0.506        0.049

##### <span style="color:MediumSlateBlue"> Анализ влияния solver оптимизатора на качество и скорость обучения модели</span>

Проверим качество и скорость сходимости модели при разных solver  
Проверку осуществим через цикл  
Чтобы модель не сходилась бесконечно с помощью модуля func_timeout  
поставим ограничение времени схождения в 10 минут

In [934]:
# подготовим данные для обучения модели

# обьявим scaler
scaler = StandardScaler()
# выполним scaler преобразование
X_train_s_balanced = scaler.fit_transform(X_train_balanced[list_ncorr_features])
X_train_s = scaler.transform(X_train[list_ncorr_features])
X_valid_s = scaler.transform(X_valid[list_ncorr_features])

# time: 10s

In [935]:
# Зададим список solvers
solvers_list = ['lbfgs', 'liblinear', 'newton-cg', 'newton-cholesky', 'sag', 'saga']

# сформируем список для заполнения
solvers_data = []

# установим ограничение на время обучения модели в 180 секунд (3 минут)
time_out = 180

for solver in solvers_list:
        # для того чтобы следить за выполнением цикла введем индикатор
        print('current solver: ', solver)

         # сформируем список для заполнения данными текушего solver
        current_solver_data = [solver]
        
        try:
                # для модуля func_time_out упакуем обучение модели в функцию try_func
                def try_func():
                        logistic_regression = linear_model.LogisticRegression(solver= solver,
                                                                  random_state=42, 
                                                                  max_iter=10000)
                        return logistic_regression.fit(X_train_s_balanced,y_train_balanced)
                    
                # фиксируем время начала
                start_time = time.time()
                
                # запускаем обучение модели с ограничением по времени
                logistic_regression = func_timeout.func_timeout(time_out, try_func)
                
                # фиксируем время окончания обучения
                end_time = time.time()
                
                # запишем время обучения модели
                current_solver_data.append(round(end_time-start_time))

                # Делаем предсказание для обучающей и валидационной выборки
                y_valid_lr_pred = logistic_regression.predict(X_valid_s)
                
                # для метрик ROC AUC делаем предсказание модели для обучающей и валидационной выборки  
                # в виде вероятности принадлежности к классу 1 
                y_train_lr_pred_proba = logistic_regression.predict_proba(X_train_s)[:,1]
                y_valid_lr_pred_proba = logistic_regression.predict_proba(X_valid_s)[:,1]

                #Считаем метрики ROC AUC yна обуающем и валидационном наборе и добавляем их в спискок
                current_solver_data.append(round(metrics.roc_auc_score(y_train, y_train_lr_pred_proba),3))
                current_solver_data.append(round(metrics.roc_auc_score(y_valid, y_valid_lr_pred_proba),3))

                #Считаем метрики для класса 0 на валидационном наборе и добавляем их в список
                current_solver_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))
                current_solver_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))


                #Считаем метрики для класса 1 на валидационном набопе и добавляем их в список
                current_solver_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))
                current_solver_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))

                # запишем данные полученные на одной итерации
                solvers_data.append(current_solver_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                solvers_pd =pd.DataFrame(
                        columns=['solver','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = solvers_data)
                # сохраняем dataframe
                solvers_pd.to_csv('data_recovery/solvers_pd.csv',index=False)
               
                # очистим output от прошедшей итерации
                clear_output()

        except func_timeout.FunctionTimedOut:
                # если время обучения привышает лимит
                # запишем в current_solver_data соотвествующую данные
                current_solver_data = [solver,'>3m',0,0,0,0,0,0]
                # добавляем полученные данные в список solvers_data
                solvers_data.append(current_solver_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                solvers_pd =pd.DataFrame(
                        columns=['solver','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = solvers_data)
                # сохраняем dataframe
                solvers_pd.to_csv('data_recovery/solvers_pd.csv',index=False)
                
                # очистим output от прошедшей итерации
                clear_output()
                # переходим к следующему solver
                pass
# очистим output
clear_output()

# сформируем данные соотвествующие лучщему ROC AUC на валидацинном наборе
best_roc_valid_data = solvers_pd[solvers_pd['roc_valid']==solvers_pd['roc_valid'].max()]

# выведем лучший результат на валидационном наборе
print('result:')
print('best solver on valid:',best_roc_valid_data.iloc[0]['solver'])
print('ROC AUC on train:', best_roc_valid_data.iloc[0]['roc_train'])
print('ROC AUC on valid:', best_roc_valid_data.iloc[0]['roc_valid'])
print('Time fit for best solver:', best_roc_valid_data.iloc[0]['time_fit'],' seconds')

# выведем полученный dataframe
solvers_pd

# time: 2m 35s

result:
best solver on valid: lbfgs
ROC AUC on train: 0.602
ROC AUC on valid: 0.611
Time fit for best solver: 0  seconds


solver  time_fit  roc_train  roc_valid  recall_0  precision_0  \
0            lbfgs         0      0.602      0.611     0.643        0.973   
1        liblinear         0      0.602      0.611     0.643        0.973   
2        newton-cg         0      0.602      0.611     0.643        0.973   
3  newton-cholesky         0      0.602      0.611     0.643        0.973   
4              sag         0      0.602      0.611     0.643        0.973   
5             saga         0      0.602      0.611     0.643        0.973   

   recall_1  precision_1  
0     0.506        0.049  
1     0.506        0.049  
2     0.506        0.049  
3     0.506        0.049  
4     0.506        0.049  
5     0.506        0.049

##### <span style="color:MediumSlateBlue">Подбор гиперпараметров модели</span>

In [1743]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'relative'
count_features = dict_spaces[feature_space]

# для работы функции corr_transform_to_force
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()

# для выбора sceler преобразвания нам понадобится словарь
dict_scalers ={
    'MinMaxScaler': MinMaxScaler(),
    'RobustScaler':RobustScaler(),
    'StandardScaler':StandardScaler()}

# настроим оптимизацию гипер параметров
def optuna_lg(trial):
  # задаем пространства поиска гиперпараметров
  solver = trial.suggest_categorical("solver", ['lbfgs', 'liblinear', 'newton-cg', 'newton-cholesky'])
  C = trial.suggest_float('C',0.01,1)
  class_0_weight = trial.suggest_float('class_0_weight',0.2,0.6)
  class_1_weight = trial.suggest_float('class_1_weight',0.2,0.6)
  threshold = trial.suggest_float('threshold',0.6,1)
  class_1_percent = trial.suggest_float('class_1_percent',0.01,0.3)
  scaler = trial.suggest_categorical("scaler", ['MinMaxScaler','RobustScaler','StandardScaler'])
  random_state = trial.suggest_int('random_state', 1, 1000000)


  # создаем модель
  optuna_log_reg = linear_model.LogisticRegression(
      solver=solver,
      C=C,
      class_weight={0:class_0_weight,1:class_1_weight},
      random_state=random_state,
      max_iter=10000)

  # с помощью функции corr_transform_to_force получим
  # список не коррелируемых признаков
  list_ncorr_features = corr_transform_to_force(corr_matrix,threshold=threshold)[1]

  # обьявим scaler
  scaler = dict_scalers[scaler]

  # сформируем данные для анализа сбалансированности обучающих данных
  X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
  y_train_pd = pd.read_csv('target/target_train.csv')

  # поготовим данные y_train_pd к работе с функцией class_1_percent_samples
  y_train_pd.set_index('id',drop=False,inplace=True)

  # подготовим данные для обучения модели
  # с помощью функции class_1_percent_samples зададим долю 
  # класса 1
  list_c1_percent_id = class_1_percent_samples(y_train_pd,class_1_percent,random_state=random_state)[:1000000]

  # подготовим данные для обучения
  X_train_s_balanced = scaler.fit_transform(X_train_pd.loc[list_c1_percent_id])
  y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

  # освободим память от "тяжелых" и ненужных файлов
  del X_train_pd, y_train_pd
  gc.collect()

  # я не воспользовался параметром timeout метода optimize потому, что  
  # optimize отставливает поиск параметров, если время обучения 
  # превышает timeout. Мне нужно чтобы поиск параметров продолжился.
  try:
    # для модуля func_time_out упакуем обучение модели в функцию try_func
    def try_func():
            return optuna_log_reg.fit(X_train_s_balanced, y_train_balanced)
    # обучаем модель с ограничением по времени 10 минут (600 секунд)
    optuna_log_reg = func_timeout.func_timeout(600, try_func)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train_s_balanced, y_train_balanced
    gc.collect()

    # загружаем тестовые наборы
    # сформируем данные для анализа сбалансированности обучающих данных
    X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
    X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()[list_ncorr_features]
    y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
    y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

    # подготовим данные для проверки модели
    X_train_s = scaler.transform(X_train)
    X_valid_s = scaler.transform(X_valid)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train, X_valid
    gc.collect()

    # делаем предсказание на обучающем и валидационном наборе и считаем метрики
    roc_train = metrics.roc_auc_score(y_train, optuna_log_reg.predict_proba(X_train_s)[:,1])
    roc_valid = metrics.roc_auc_score(y_valid, optuna_log_reg.predict_proba(X_valid_s)[:,1])
    f1_score = metrics.f1_score(y_valid, optuna_log_reg.predict(X_valid_s))
    recall_1 = metrics.recall_score(y_valid, optuna_log_reg.predict(X_valid_s),average=None,zero_division=0)[1]
    precision_1 = metrics.precision_score(y_valid, optuna_log_reg.predict(X_valid_s),average=None,zero_division=0)[1]

    # удаляем крупные файлы чтобы высвободить память 
    del X_train_s, X_valid_s, y_train, y_valid
    gc.collect()

  except func_timeout.FunctionTimedOut:
    # удаляем крупные файлы чтобы высвободить память 
    del X_train_s_balanced, y_train_balanced
    gc.collect()
    
    # фиксируем пустые значения метрик
    roc_train = 0
    roc_valid = 0
    f1_score = 0
    recall_1 = 0
    precision_1 = 0
    pass

  return roc_train, roc_valid, f1_score, recall_1, precision_1

In [1744]:
# cоздаем объект исследования
# чтобы модель не переобучалась минимизируем roc_train 
# и максимизируем roc_valid
optuna_study_lg = optuna.create_study(study_name='LogisticRegression_'+feature_space+'_stat', 
                               directions=['maximize','maximize','maximize','maximize','maximize'], 
                               sampler=optuna.samplers.TPESampler(),
                               pruner='Hyperband',
                               storage='sqlite:///optuna_studies.db',
                               load_if_exists=True)
# optuna.delete_study(study_name='LogisticRegression_'+feature_space+'_stat', storage='sqlite:///optuna_studies.db')

[I 2025-04-19 14:52:46,587] Using an existing study with name 'LogisticRegression_relative_stat' instead of creating a new one.


In [938]:
# ищем лучшую комбинацию гиперпараметров n_trials раз
optuna_study_lg.optimize(optuna_lg, n_trials=300)

[I 2025-04-18 02:51:32,734] Trial 0 finished with values: [0.6074693177726718, 0.6135149493844037, 0.0015841584158415843, 0.0007990411506192569, 0.09090909090909091] and parameters: {'solver': 'lbfgs', 'C': 0.5874359089659255, 'class_0_weight': 0.29069430687829495, 'class_1_weight': 0.31732608311327287, 'threshold': 0.6777440306863617, 'class_1_percent': 0.10375964052673962, 'scaler': 'RobustScaler', 'random_state': 189453}.
[I 2025-04-18 02:51:37,976] Trial 1 finished with values: [0.6110776299461078, 0.6186207429522905, 0.016158648549394052, 0.008789452656811825, 0.1] and parameters: {'solver': 'newton-cg', 'C': 0.42010009835441176, 'class_0_weight': 0.27571666635931225, 'class_1_weight': 0.37707270646030583, 'threshold': 0.804161826661133, 'class_1_percent': 0.18249364536057874, 'scaler': 'MinMaxScaler', 'random_state': 719872}.
[I 2025-04-18 02:51:43,109] Trial 2 finished with values: [0.6158237641469814, 0.6226257875104836, 0.0015766653527788726, 0.0007990411506192569, 0.058823529

In [1745]:
# из полученного результат соврмируем Data Frame
optuna_study_lg_pd = optuna_study_lg.trials_dataframe().dropna()
# переименуем столбы
optuna_study_lg_pd.rename(columns={
    'values_0': 'roc_train',
    'values_1': 'roc_valid',
    'values_2': 'f1_score',
    'values_3': 'recall_1',
    'values_4': 'precision_1'
},inplace=True)
# Выделим время потраченное на обучение модели
optuna_study_lg_pd.tail()

number  roc_train  roc_valid  f1_score  recall_1  precision_1  \
295     295   0.623624   0.628887  0.022214  0.011986     0.151515   
296     296   0.623404   0.628623  0.089469  0.102677     0.079272   
297     297   0.623121   0.628729  0.095770  0.143827     0.071785   
298     298   0.610508   0.617583  0.102064  0.236117     0.065102   
299     299   0.626001   0.631085  0.107074  0.267279     0.066947   

                datetime_start          datetime_complete  \
295 2025-04-18 03:27:06.246233 2025-04-18 03:27:15.569472   
296 2025-04-18 03:27:15.575195 2025-04-18 03:27:24.969114   
297 2025-04-18 03:27:24.975329 2025-04-18 03:27:33.628769   
298 2025-04-18 03:27:33.634828 2025-04-18 03:27:40.998900   
299 2025-04-18 03:27:41.004987 2025-04-18 03:28:01.594769   

                  duration  params_C  params_class_0_weight  \
295 0 days 00:00:09.323239  0.883911               0.334015   
296 0 days 00:00:09.393919  0.238399               0.334212   
297 0 days 00:00:08.653440  0.123232               0.307787   
298 0 days 00:00:07.364072  0.227441               0.274224   
299 0 days 00:00:20.589782  0.857650               0.240657   

     params_class_1_percent  params_class_1_weight  params_random_state  \
295                0.242024               0.217082               640639   
296                0.239999               0.556233               751078   
297                0.242490               0.584346               520531   
298                0.247778               0.573768               902369   
299                0.221761               0.583542               462384   

    params_scaler params_solver  params_threshold     state  
295  RobustScaler         lbfgs          0.981231  COMPLETE  
296  RobustScaler         lbfgs          0.978604  COMPLETE  
297  RobustScaler         lbfgs          0.973169  COMPLETE  
298  MinMaxScaler         lbfgs          0.807351  COMPLETE  
299  RobustScaler         lbfgs          0.999546  COMPLETE

In [1746]:
# покаждем статистику обучения
print('Максимальное значение метрики ROC AUC на валидационном наборе:',round(optuna_study_lg_pd['roc_valid'].max(),3))
print('Среднее значение метрики ROC AUC на валидационном наборе:',round(optuna_study_lg_pd['roc_valid'].mean(),3))
print('Максимальное значение метрики f1_score на валидационном наборе:',round(optuna_study_lg_pd['f1_score'].max(),3))
print('Среднее значение метрики f1_score на валидационном наборе:',round(optuna_study_lg_pd['f1_score'].mean(),3))
print('Максимальное значение метрики recall_1 на валидационном наборе:',round(optuna_study_lg_pd['recall_1'].max(),3))
print('Среднее значение метрики recall_1 на валидационном наборе:',round(optuna_study_lg_pd['recall_1'].mean(),3))
print('Максимальное значение метрики precision_1 на валидационном наборе:',round(optuna_study_lg_pd['precision_1'].max(),3))
print('Среднее значение метрики precision_1 на валидационном наборе:',round(optuna_study_lg_pd['precision_1'].mean(),3))

Максимальное значение метрики ROC AUC на валидационном наборе: 0.631
Среднее значение метрики ROC AUC на валидационном наборе: 0.625
Максимальное значение метрики f1_score на валидационном наборе: 0.108
Среднее значение метрики f1_score на валидационном наборе: 0.073
Максимальное значение метрики recall_1 на валидационном наборе: 0.559
Среднее значение метрики recall_1 на валидационном наборе: 0.149
Максимальное значение метрики precision_1 на валидационном наборе: 0.333
Среднее значение метрики precision_1 на валидационном наборе: 0.084


In [1750]:
# Визуализируем метрики полученные при optuna оптимизации
fig = px.scatter(
    data_frame=optuna_study_lg_pd[(optuna_study_lg_pd['roc_valid']>0.9999*optuna_study_lg_pd['roc_valid'].max())],
    x='number', #ось абсцисс
    y=['roc_train','roc_valid','recall_1','precision_1','f1_score'], #ось ординат
)
fig.update_layout(
    title ={
        'text':'Зависимость качества модели от trials optuna', # Имя рабочей плоскости
        'font':{'size':35,'family':"Times New Roman"}, # размер и стиль написания имени рабочей плоскости
        'x':0.5, # Смешение имени по оси "x" на половину рабочей плоскости
        },
    height =800,# Высота рабочей плоскости
    width = 1350, # Ширина рабочей плоскости
    bargap=0.2, # Добавил расстояния между столбами гистограммы
    xaxis_title='trials optuna',
    yaxis_title='Величина метрики')
fig.update_xaxes(showspikes=True)
fig.update_yaxes(showspikes=True)

fig.show()

<span style="color:Blue">

Вывод:  

Их всех выбираем точку $number =236$.   
В этой точке самые оптимальные значения $recall$ и $precision$.  
Посмотрим каким значениям гиперпараметров соотвествует выбранная точка.

In [1751]:
# определим номер лучшге варианта
best_optuna_number = 236

# сформируем словарь лучших гипирпарметров RandomForestClassifier
best_param_lr = {
    'solver' : optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_solver'].iloc[0],
    'C' : round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_C'].iloc[0],3),
    'class_weight' : {0:round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_class_0_weight'].iloc[0],3),
                      1:round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_class_1_weight'].iloc[0],3)},
    }

# создадим перменные
best_threshold = optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_threshold'].iloc[0]
best_scaler = optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_scaler'].iloc[0]
best_class_1_percent = optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_class_1_percent'].iloc[0]
best_random_state = optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_random_state'].iloc[0]

# Выведем принятые наилучшие праметры
print('best solver:',best_param_lr['solver'])
print('best C:',best_param_lr['C'])
print('best class 0 weight:',best_param_lr['class_weight'][0])
print('best class 1 weight:',best_param_lr['class_weight'][1])

print('best class 1 percent:',round(best_class_1_percent,3))
print('best scaler:',best_scaler)
print('best threshold:',round(best_threshold,3))
print('best best random state:',best_random_state)
print('time for best train:',round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['duration'].iloc[0].seconds/60),'minutes')

print()
print('ROC AUC на обучающем наборе:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['roc_train'].iloc[0],3))
print('ROC AUC на валидационном наборе:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['roc_valid'].iloc[0],3))
print('precision класса 1:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['precision_1'].iloc[0],3))
print('recall класса 1:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['recall_1'].iloc[0],3))


best solver: newton-cg
best C: 0.863
best class 0 weight: 0.346
best class 1 weight: 0.588
best class 1 percent: 0.293
best scaler: StandardScaler
best threshold: 1.0
best best random state: 189149
time for best train: 0 minutes

ROC AUC на обучающем наборе: 0.626
ROC AUC на валидационном наборе: 0.631
precision класса 1: 0.066
recall класса 1: 0.279


##### <span style="color:MediumSlateBlue">Обучение модели с лучшими параметрами</span>

In [1752]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'relative'
count_features = dict_spaces[feature_space]

# для работы функции corr_transform_to_force
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()

# подготовим данные
# для выбора sceler преобразвания нам понадобится словарь
dict_scalers ={
    'MinMaxScaler': MinMaxScaler(),
    'RobustScaler':RobustScaler(),
    'StandardScaler':StandardScaler(),
}

# с помощью функции corr_transform_to_force получим
# список не коррелируемых признаков
list_ncorr_features = corr_transform_to_force(corr_matrix,threshold=best_threshold)[1]

# обьявим scaler
scaler = dict_scalers[best_scaler]

# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
y_train_pd = pd.read_csv('target/target_train.csv')

# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)

# подготовим данные для обучения модели
# с помощью функции class_1_percent_samples зададим долю 
# класса 1
list_c1_percent_id = class_1_percent_samples(y_train_pd,best_class_1_percent,random_state=best_random_state)[:1000000]

# подготовим данные для обучения
X_train_s_balanced = scaler.fit_transform(X_train_pd.loc[list_c1_percent_id])
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

# освободим память от "тяжелых" и ненужных файлов
del X_train_pd, y_train_pd
gc.collect()


# обучаем модель LogisticRegression с наилучшеми параметрами
logistic_regression = linear_model.LogisticRegression(
        **best_param_lr,
        random_state=42,
        max_iter=10000)
logistic_regression.fit(X_train_s_balanced, y_train_balanced)

# удаляем крупные файлы чтобы высвободить память 
del X_train_s_balanced, y_train_balanced
gc.collect()

# загружаем тестовые наборы
# сформируем данные для анализа сбалансированности обучающих данных
X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()[list_ncorr_features]
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

# подготовим данные для проверки модели
X_train_s = scaler.transform(X_train)
X_valid_s = scaler.transform(X_valid)

# удаляем крупные файлы чтобы высвободить память 
del X_train, X_valid
gc.collect()

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_lr_pred_proba = logistic_regression.predict_proba(X_train_s)[:,1]
y_valid_lr_pred_proba = logistic_regression.predict_proba(X_valid_s)[:,1]

# Делаем предсказание для валидационной выборки
y_valid_lr_pred = logistic_regression.predict(X_valid_s)

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_lr_pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_lr_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_lr_pred,zero_division=0))

# time: 2m 30s

ROC AUC на обучающем наборе 0.626
ROC AUC на валидационном наборе 0.631
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.97      0.86      0.91     68747
           1       0.07      0.28      0.11      2503

    accuracy                           0.84     71250
   macro avg       0.52      0.57      0.51     71250
weighted avg       0.94      0.84      0.88     71250



#### <span style="color:MediumBlue">Построение модели Random Forest Classifier</span>

##### <span style="color:MediumSlateBlue">Формирование данных для обучения</span>

Анализ исходных данных, в частности target, показал что представленные данные   
имееют перекос: 96% клиентов у которых не случился дефолт (flag = 0),    
против 4 % - для которых произошел дефолт (flag = 1).  
С помощью функции class_1_percent_samples, сформируем сбаланисрованную выборку  
для обучения моделей.
За основу сбалансировных данных возьмем данные клиентов с дефолтом  
и к ним будем добирать необходимое количество клиентов до сбалансированности. 


Функция class_1_percent_samples принемает две переменные:
- target_data - массив с id и целевой переменной
- class_1_percent - процент класса 1 в результирующем массиве

In [956]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'relative'
count_features = dict_spaces[feature_space]

In [957]:
# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

In [958]:
# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)
y_train_pd.head(4)

id  flag
id                    
1825800  1825800     0
2166483  2166483     0
2534345  2534345     0
1803283  1803283     0

In [959]:
# взглянем на сблансиорованность данных в y_train
y_train_pd['flag'].value_counts(normalize=True)

flag
0    0.964242
1    0.035758
Name: proportion, dtype: float64

In [960]:
# сбалансируем данные в y_train_pd
list_c1_percent_id = class_1_percent_samples(y_train_pd,0.5)
# list_c1_percent_features - список 'id' из y_train_pd соотвествующих  
# заданному проценту класса 1
len(list_c1_percent_id)

45860

In [961]:
# проверим сбалансированность полученного y_train
y_train_pd.loc[list_c1_percent_id]['flag'].value_counts(normalize=True)

flag
1    0.5
0    0.5
Name: proportion, dtype: float64

В отличие от данных в *transform_data_torow*, где модели показываеются последние N  
операций клиента, в данные в *transform_data_stat* сфомированы из различных статистических   
характеристик ряда определяющего клиентскую историю в банке. 

Соотвественно, если в данных *transform_data_torow* была сильная корреляция между признаками,  
то я не смог бы ее убрать, иначе потярется смысл "показать последовательный ряд в историии клиента".  
Признаки в *transform_data_stat* не имеют такой особенности. Поэтому, необходимо проанализировать  
данные в *transform_data_stat* и, в случае сильной коррреляции признаков, устранить ее.

In [962]:
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()
corr_matrix.shape

(103, 103)

In [963]:
# с помощью функции corr_transrom_to_power получим
# силу корреляции матрицы и список не коррелируемых признаков

# для начального анализа зададим порог силы корреляции, при котором признаки 
# будут отнесены к "сильно скоррелированными" равным 0.6
ncorr_matrix,list_ncorr_features,corr_power =corr_transform_to_force(corr_matrix,threshold=0.6)

# Выведем результаты преобразования
print('Исходное количество признаков: ', corr_matrix.shape[0])
print('Количество не коррелируемых признаков: ', len(list_ncorr_features))
# сила корреляции признаков
print('Отношение коррелируемых исходному количеству признаков (сила корреляции): ',corr_power)

Исходное количество признаков:  103
Количество не коррелируемых признаков:  27
Отношение коррелируемых исходному количеству признаков (сила корреляции):  0.738


In [964]:
# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']
# сформируем данные для проверики модели
# сформируем данные для анализа сбалансированности обучающих данных
X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()
y_train = pd.read_csv('target/target_train.csv')['flag']
X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()
y_valid = pd.read_csv('target/target_valid.csv')['flag']

In [965]:
# посмотрим на структуру данных в X_train_balanced
X_train_balanced.head(4)

f1    f2      f3      f4      f5      f6      f7   f8     f9  f10  \
id                                                                             
2335465  17.0  15.0  14.235  12.550  12.550  15.938  14.235  0.0  4.180  1.0   
390270    6.0  16.0  12.333   0.000   0.000  15.784  12.333  0.0  5.793  0.0   
2494034  14.0  13.0  12.500  11.422  11.422  15.822  12.500  0.0  4.355  3.0   
2018674  15.0   7.0  14.933  14.748  14.748  15.902  14.933  0.0  2.112  9.0   

         ...   f94  f95  f96  f97  f98  f99  f100  f101   f102  f103  
id       ...                                                          
2335465  ...  0.00  1.0  1.0  1.0  1.0  1.0   1.0  1.00  0.000   1.0  
390270   ...  0.00  1.0  1.0  1.0  1.0  1.0   1.0  1.00  0.000   1.0  
2494034  ...  0.35  0.0  1.0  1.0  1.0  1.0   1.0  0.86  0.132   0.5  
2018674  ...  0.34  0.0  1.0  1.0  1.0  1.0   1.0  0.87  0.124   0.5  

[4 rows x 103 columns]

In [966]:
# посмотрим на структуру данных в y_train_balanced
y_train_balanced.head(4)

id
2335465    1
390270     1
2494034    1
2018674    1
Name: flag, dtype: int64

In [967]:
# проверим что выборки действительно совпадают по id
X_train_balanced.index.to_list() == y_train_balanced.index.to_list()

True

##### <span style="color:MediumSlateBlue">Baseline обучение модели RandomForestClassifier</span>

In [968]:
# обучаем модель логистической регрессии
# чтобы модель пыталась найти связь во всех признаках
random_forest = RandomForestClassifier(random_state=42, n_jobs=-1)
random_forest.fit(X_train_balanced[list_ncorr_features],y_train_balanced)

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_rf__pred_proba = random_forest.predict_proba(X_train[list_ncorr_features])[:,1]
y_valid_rf_pred_proba = random_forest.predict_proba(X_valid[list_ncorr_features])[:,1]

# Делаем предсказание для валидационной выборки
y_valid_rf_pred = random_forest.predict(X_valid[list_ncorr_features])

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_rf__pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_rf_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_rf_pred))

# time: 17s

ROC AUC на обучающем наборе 0.799
ROC AUC на валидационном наборе 0.59
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.97      0.56      0.71     68747
           1       0.05      0.58      0.09      2503

    accuracy                           0.56     71250
   macro avg       0.51      0.57      0.40     71250
weighted avg       0.94      0.56      0.69     71250



##### <span style="color:MediumSlateBlue">Подбор гиперпараметров модели</span>

In [1753]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'relative'
count_features = dict_spaces[feature_space]

# для работы функции corr_transform_to_force
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()

# настроим оптимизацию гипер параметров
def optuna_rf(trial):
  # задаем пространства поиска гиперпараметров
  # задаем пространства поиска гиперпараметров
  n_estimators = trial.suggest_int('n_estimators', 40, 100,step = 5)
  criterion = trial.suggest_categorical('criterion',['gini', 'entropy', 'log_loss'])
  max_depth = trial.suggest_int('max_depth', 10, 30,step = 1)
  min_samples_split = trial.suggest_int('min_samples_split', 5, 15,step = 1)
  min_samples_leaf = trial.suggest_int('min_samples_leaf', 5, 15,step = 1)
  max_features = trial.suggest_float('max_features',0.4,0.8)
  max_samples = trial.suggest_float('max_samples',0.4,0.8)
  class_0_weight = trial.suggest_float('class_0_weight',0.1,1)
  class_1_weight = trial.suggest_float('class_1_weight',0.1,1)
  threshold = trial.suggest_float('threshold',0.4,0.8)
  class_1_percent = trial.suggest_float('class_1_percent',0.01,0.5)
  random_state = trial.suggest_int('random_state', 1, 1000000)


  # создаем модель
  optuna_random_forest = RandomForestClassifier(
      n_estimators = n_estimators, 
      criterion = criterion,
      max_depth = max_depth,
      min_samples_split = min_samples_split,  
      min_samples_leaf = min_samples_leaf,
      max_features=max_features,
      max_samples=max_samples,
      class_weight={0:class_0_weight,1:class_1_weight},
      n_jobs=-1,
      random_state=42)

  # с помощью функции corr_transform_to_force получим
  # список не коррелируемых признаков
  list_ncorr_features = corr_transform_to_force(corr_matrix,threshold=threshold)[1]

  # сформируем данные для анализа сбалансированности обучающих данных
  X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
  y_train_pd = pd.read_csv('target/target_train.csv')

  # поготовим данные y_train_pd к работе с функцией class_1_percent_samples
  y_train_pd.set_index('id',drop=False,inplace=True)

  # подготовим данные для обучения модели
  # с помощью функции class_1_percent_samples зададим долю 
  # класса 1
  list_c1_percent_id = class_1_percent_samples(y_train_pd,class_1_percent,random_state=random_state)[:1000000]

  # подготовим данные для обучения
  X_train_balanced = X_train_pd.loc[list_c1_percent_id]
  y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']

  # освободим память от "тяжелых" и ненужных файлов
  del X_train_pd, y_train_pd
  gc.collect()

  # я не воспользовался параметром timeout метода optimize потому, что  
  # optimize отставливает поиск параметров, если время обучения 
  # превышает timeout. Мне нужно чтобы поиск параметров продолжился.
  try:
    # для модуля func_time_out упакуем обучение модели в функцию try_func
    def try_func():
            return optuna_random_forest.fit(X_train_balanced, y_train_balanced)
    # обучаем модель с ограничением по времени 10 минут (600 секунд)
    optuna_random_forest = func_timeout.func_timeout(600, try_func)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train_balanced, y_train_balanced
    gc.collect()

    # загружаем тестовые наборы
    # сформируем данные для анализа сбалансированности обучающих данных
    X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
    X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()[list_ncorr_features]
    y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
    y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()
    
    # делаем предсказание на обучающем и валидационном наборе
    #Считаем метрики для класса 1 добавляем их в список
    roc_train = metrics.roc_auc_score(y_train, optuna_random_forest.predict_proba(X_train)[:,1])
    roc_valid = metrics.roc_auc_score(y_valid, optuna_random_forest.predict_proba(X_valid)[:,1])
    f1_score = metrics.f1_score(y_valid, optuna_random_forest.predict(X_valid))
    recall_1 = metrics.recall_score(y_valid, optuna_random_forest.predict(X_valid),average=None,zero_division=0)[1]
    precision_1 = metrics.precision_score(y_valid, optuna_random_forest.predict(X_valid),average=None,zero_division=0)[1]

    # удаляем крупные файлы чтобы высвободить память 
    del X_train, X_valid, y_train, y_valid
    gc.collect()

  except func_timeout.FunctionTimedOut:
    # удаляем крупные файлы чтобы высвободить память 
    del X_train_balanced, y_train_balanced
    gc.collect()
    
    # фиксируем пустые значения метрик
    roc_train = 0
    roc_valid = 0
    f1_score = 0
    recall_1 = 0
    precision_1 = 0
    pass

  return roc_train, roc_valid, f1_score, recall_1, precision_1

In [1754]:
# cоздаем объект исследования
optuna_study_rf = optuna.create_study(study_name= 'RandomForestClassifier_'+feature_space+'_stat', 
                               directions=['maximize','maximize','maximize','maximize','maximize'], 
                               sampler=optuna.samplers.TPESampler(),
                               pruner='Hyperband',
                               storage='sqlite:///optuna_studies.db',
                               load_if_exists=True)
# на случай удаления 
# optuna.delete_study(study_name='RandomForestClassifier_'+feature_space+'_stat', storage='sqlite:///optuna_studies.db')

[I 2025-04-19 14:55:25,639] Using an existing study with name 'RandomForestClassifier_relative_stat' instead of creating a new one.


In [971]:
# ищем лучшую комбинацию гиперпараметров n_trials раз
optuna_study_rf.optimize(optuna_rf, n_trials=300)

[I 2025-04-18 03:28:35,776] Trial 0 finished with values: [0.6442407857183684, 0.627629063983679, 0.04045092838196287, 0.024370755093887336, 0.1189083820662768] and parameters: {'n_estimators': 50, 'criterion': 'entropy', 'max_depth': 10, 'min_samples_split': 6, 'min_samples_leaf': 11, 'max_features': 0.6784403438344064, 'max_samples': 0.44206699677074734, 'class_0_weight': 0.8321004378883985, 'class_1_weight': 0.3243523226433118, 'threshold': 0.49757678711102243, 'class_1_percent': 0.4145842914281652, 'random_state': 330182}.
[I 2025-04-18 03:28:41,363] Trial 1 finished with values: [0.6806691694930489, 0.6382419267562736, 0.02134959969500572, 0.011186576108669596, 0.23333333333333334] and parameters: {'n_estimators': 95, 'criterion': 'gini', 'max_depth': 21, 'min_samples_split': 5, 'min_samples_leaf': 12, 'max_features': 0.6479658375994508, 'max_samples': 0.40803015912467844, 'class_0_weight': 0.5904881484792392, 'class_1_weight': 0.13909103154084285, 'threshold': 0.5983189188436976,

In [1755]:
# из полученного результат соврмируем Data Frame
optuna_study_rf_pd = optuna_study_rf.trials_dataframe().dropna()
# переименуем столбы
optuna_study_rf_pd.rename(columns={
    'values_0': 'roc_train',
    'values_1': 'roc_valid',
    'values_2': 'f1_score',
    'values_3': 'recall_1',
    'values_4': 'precision_1'
},inplace=True)
optuna_study_rf_pd.tail()

number  roc_train  roc_valid  f1_score  recall_1  precision_1  \
295     295   0.792046   0.621711  0.086911  0.664403     0.046497   
296     296   0.791079   0.631977  0.098369  0.515781     0.054369   
297     297   0.689631   0.652800  0.109810  0.163004     0.082792   
298     298   0.688324   0.650067  0.110436  0.304834     0.067433   
299     299   0.676797   0.654598  0.110362  0.431882     0.063264   

                datetime_start          datetime_complete  \
295 2025-04-18 04:10:06.905160 2025-04-18 04:10:18.818024   
296 2025-04-18 04:10:18.824114 2025-04-18 04:10:30.933059   
297 2025-04-18 04:10:30.938749 2025-04-18 04:10:41.966826   
298 2025-04-18 04:10:41.972145 2025-04-18 04:10:52.506702   
299 2025-04-18 04:10:52.512543 2025-04-18 04:11:02.872759   

                  duration  params_class_0_weight  ...  params_criterion  \
295 0 days 00:00:11.912864               0.129488  ...           entropy   
296 0 days 00:00:12.108945               0.181143  ...           entropy   
297 0 days 00:00:11.028077               0.321415  ...           entropy   
298 0 days 00:00:10.534557               0.303820  ...           entropy   
299 0 days 00:00:10.360216               0.297039  ...           entropy   

     params_max_depth params_max_features  params_max_samples  \
295                23            0.548341            0.782887   
296                25            0.552123            0.763812   
297                11            0.552543            0.761889   
298                11            0.548127            0.759363   
299                10            0.555242            0.748801   

     params_min_samples_leaf  params_min_samples_split  params_n_estimators  \
295                        6                        14                   85   
296                        5                        15                   90   
297                        6                        15                   90   
298                        6                        15                   85   
299                        7                        15                   85   

     params_random_state  params_threshold     state  
295               382735          0.786575  COMPLETE  
296               458090          0.776597  COMPLETE  
297               367223          0.798379  COMPLETE  
298               373096          0.793854  COMPLETE  
299               396833          0.797439  COMPLETE  

[5 rows x 22 columns]

In [1756]:
# покаждем статистику обучения
print('Максимальное значение метрики ROC AUC на валидационном наборе:',round(optuna_study_rf_pd['roc_valid'].max(),3))
print('Среднее значение метрики ROC AUC на валидационном наборе:',round(optuna_study_rf_pd['roc_valid'].mean(),3))
print('Максимальное значение метрики f1_score на валидационном наборе:',round(optuna_study_rf_pd['f1_score'].max(),3))
print('Среднее значение метрики f1_score на валидационном наборе:',round(optuna_study_rf_pd['f1_score'].mean(),3))
print('Максимальное значение метрики recall_1 на валидационном наборе:',round(optuna_study_rf_pd['recall_1'].max(),3))
print('Среднее значение метрики recall_1 на валидационном наборе:',round(optuna_study_rf_pd['recall_1'].mean(),3))
print('Максимальное значение метрики precision_1 на валидационном наборе:',round(optuna_study_rf_pd['precision_1'].max(),3))
print('Среднее значение метрики precision_1 на валидационном наборе:',round(optuna_study_rf_pd['precision_1'].mean(),3))

Максимальное значение метрики ROC AUC на валидационном наборе: 0.657
Среднее значение метрики ROC AUC на валидационном наборе: 0.636
Максимальное значение метрики f1_score на валидационном наборе: 0.115
Среднее значение метрики f1_score на валидационном наборе: 0.085
Максимальное значение метрики recall_1 на валидационном наборе: 0.993
Среднее значение метрики recall_1 на валидационном наборе: 0.364
Максимальное значение метрики precision_1 на валидационном наборе: 0.233
Среднее значение метрики precision_1 на валидационном наборе: 0.069


In [1759]:
# Построим зависимость метрик качества модели от number

fig = px.scatter(
    data_frame=optuna_study_rf_pd[(optuna_study_rf_pd['roc_valid']>=0.999*optuna_study_rf_pd['roc_valid'].max())],
    x='number', #ось абсцисс
    y=['roc_valid','roc_train','precision_1','recall_1','f1_score'], #ось ординат
)
fig.update_layout(
    title ={
        'text':'Зависимость качества модели от trials optuna', # Имя рабочей плоскости
        'font':{'size':35,'family':"Times New Roman"}, # размер и стиль написания имени рабочей плоскости
        'x':0.5, # Смешение имени по оси "x" на половину рабочей плоскости
        },
    height =800,# Высота рабочей плоскости
    width = 1350, # Ширина рабочей плоскости
    bargap=0.2, # Добавил расстояния между столбами гистограммы
    xaxis_title='trials optuna',
    yaxis_title='Величина параметра')
fig.update_xaxes(showspikes=True)
fig.update_yaxes(showspikes=True)

fig.show()

<span style="color:Blue">

Вывод:  

Их всех выбираем точку $number =48$.   
Не смотря на, то что в этой точке модель подает признаки переобучеености,  
в этой точке оптимальные значения метрик $recall_1$ и $precision_1$, а  
также относительно высокая метрика $ROC AUC$.   
Посмотрим каким значениям гиперпараметров соотвествует выбраннаяточка.

In [1760]:
# определим номер лучшге варианта
best_optuna_number = 48

# сформируем словарь лучших гипирпарметров RandomForestClassifier
best_param_rf = {
    'n_estimators' : int(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_n_estimators'].iloc[0]),
    'criterion': optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_criterion'].iloc[0],
    'max_depth' : int(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_max_depth'].iloc[0]),
    'min_samples_split': int(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_min_samples_split'].iloc[0]),
    'min_samples_leaf' : int(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_min_samples_leaf'].iloc[0]),
    'max_features': optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_max_features'].iloc[0],
    'max_samples' : optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_max_samples'].iloc[0],
    'class_weight' : {0:optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_class_0_weight'].iloc[0],
                      1:optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_class_1_weight'].iloc[0]}
    }

# определим перменные для лучших значений параметров
best_threshold = optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_threshold'].iloc[0]
best_class_1_percent = optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_class_1_percent'].iloc[0]
best_random_state = optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_random_state'].iloc[0]


# Выведем принятые наилучшие праметры
print('best n estimators:',best_param_rf['n_estimators'])
print('best criterion:',best_param_rf['criterion'])
print('best max depth:',best_param_rf['max_depth'])
print('best min samples split:',best_param_rf['min_samples_split'])
print('best min samples leaf:',best_param_rf['min_samples_leaf'])
print('best max features(%):',round(best_param_rf['max_features'],3))
print('best max samples(%):',round(best_param_rf['max_samples'],3))
print('best class 0 weight:',round(best_param_rf['class_weight'][0],3))
print('best class 1 weight:',round(best_param_rf['class_weight'][1],3))

print('best class 1 percent:',round(best_class_1_percent,3))
print('best threshold:',round(best_threshold,3))
print('best random state:', best_random_state)
print('time for best train:',round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['duration'].iloc[0].seconds/60),'minutes')

print()
print('ROC AUC на обучающем наборе:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['roc_train'].iloc[0],3))
print('ROC AUC на валидационном наборе:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['roc_valid'].iloc[0],3))
print('precision класса 1:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['precision_1'].iloc[0],3))
print('recall класса 1:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['recall_1'].iloc[0],3))

best n estimators: 45
best criterion: entropy
best max depth: 10
best min samples split: 13
best min samples leaf: 13
best max features(%): 0.564
best max samples(%): 0.742
best class 0 weight: 0.613
best class 1 weight: 0.909
best class 1 percent: 0.054
best threshold: 0.778
best random state: 309434
time for best train: 0 minutes

ROC AUC на обучающем наборе: 0.685
ROC AUC на валидационном наборе: 0.657
precision класса 1: 0.0
recall класса 1: 0.0


##### <span style="color:MediumSlateBlue">Обучение модели с лучшими параметрами</span>

In [1761]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'relative'
count_features = dict_spaces[feature_space]

# для работы функции corr_transform_to_force
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()

# с помощью функции corr_transform_to_force получим
# список не коррелируемых признаков
list_ncorr_features = corr_transform_to_force(corr_matrix,threshold=best_threshold)[1]

# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
y_train_pd = pd.read_csv('target/target_train.csv')

# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)

# подготовим данные для обучения модели
# с помощью функции class_1_percent_samples зададим долю 
# класса 1
list_c1_percent_id = class_1_percent_samples(y_train_pd,best_class_1_percent,random_state=best_random_state)[:1000000]

# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']

# освободим память от "тяжелых" и ненужных файлов
del X_train_pd, y_train_pd
gc.collect()


# обучаем модель RandomForestClassifier с наилучшеми параметрами
random_forest = RandomForestClassifier(
        **best_param_rf,
        n_jobs=-1,
        random_state=42)
random_forest.fit(X_train_balanced, y_train_balanced)

# удаляем крупные файлы чтобы высвободить память 
del X_train_balanced, y_train_balanced
gc.collect()

# загружаем тестовые наборы
# сформируем данные для анализа сбалансированности обучающих данных
X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()[list_ncorr_features]
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_rf_pred_proba = random_forest.predict_proba(X_train)[:,1]
y_valid_rf_pred_proba = random_forest.predict_proba(X_valid)[:,1]

# Делаем предсказание для валидационной выборки
y_valid_rf_pred = random_forest.predict(X_valid)

# удаляем крупные файлы чтобы высвободить память 
del X_train, X_valid
gc.collect()

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_rf_pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_rf_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_rf_pred,zero_division=0))

# time: 5m 30s

ROC AUC на обучающем наборе 0.685
ROC AUC на валидационном наборе 0.657
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.96      1.00      0.98     68747
           1       0.00      0.00      0.00      2503

    accuracy                           0.96     71250
   macro avg       0.48      0.50      0.49     71250
weighted avg       0.93      0.96      0.95     71250



#### <span style="color:MediumBlue">Построение модели Gradient Boosting Classifier</span>

##### <span style="color:MediumSlateBlue">Формирование данных для обучения</span>

Анализ исходных данных, в частности target, показал что представленные данные   
имееют перекос: 96% клиентов у которых не случился дефолт (flag = 0),    
против 4 % - для которых произошел дефолт (flag = 1).  
С помощью функции class_1_percent_samples, сформируем сбаланисрованную выборку  
для обучения моделей.
За основу сбалансировных данных возьмем данные клиентов с дефолтом  
и к ним будем добирать необходимое количество клиентов до сбалансированности. 


Функция class_1_percent_samples принемает две переменные:
- target_data - массив с id и целевой переменной
- class_1_percent - процент класса 1 в результирующем массиве

In [988]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'relative'
count_features = dict_spaces[feature_space]

In [989]:
# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

In [990]:
# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)
y_train_pd.head(4)

id  flag
id                    
1825800  1825800     0
2166483  2166483     0
2534345  2534345     0
1803283  1803283     0

In [991]:
# взглянем на сблансиорованность данных в y_train
y_train_pd['flag'].value_counts(normalize=True)

flag
0    0.964242
1    0.035758
Name: proportion, dtype: float64

In [992]:
# сбалансируем данные в y_train_pd
list_c1_percent_id = class_1_percent_samples(y_train_pd,0.5)
# list_c1_percent_features - список 'id' из y_train_pd соотвествующих  
# заданному проценту класса 1
len(list_c1_percent_id)

45860

In [993]:
# проверим сбалансированность полученного y_train
y_train_pd.loc[list_c1_percent_id]['flag'].value_counts(normalize=True)

flag
1    0.5
0    0.5
Name: proportion, dtype: float64

В отличие от данных в *transform_data_torow*, где модели показываеются последние N  
операций клиента, в данные в *transform_data_stat* сфомированы из различных статистических   
характеристик ряда определяющего клиентскую историю в банке. 

Соотвественно, если в данных *transform_data_torow* была сильная корреляция между признаками,  
то я не смог бы ее убрать, иначе потярется смысл "показать последовательный ряд в историии клиента".  
Признаки в *transform_data_stat* не имеют такой особенности. Поэтому, необходимо проанализировать  
данные в *transform_data_stat* и, в случае сильной коррреляции признаков, устранить ее.

In [994]:
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()
corr_matrix.shape

(103, 103)

In [995]:
# с помощью функции corr_transrom_to_power получим
# силу корреляции матрицы и список не коррелируемых признаков

# для начального анализа зададим порог силы корреляции, при котором признаки 
# будут отнесены к "сильно скоррелированными" равным 0.6
ncorr_matrix,list_ncorr_features,corr_power =corr_transform_to_force(corr_matrix,threshold=0.6)

# Выведем результаты преобразования
print('Исходное количество признаков: ', corr_matrix.shape[0])
print('Количество не коррелируемых признаков: ', len(list_ncorr_features))
# сила корреляции признаков
print('Отношение коррелируемых исходному количеству признаков (сила корреляции): ',corr_power)

Исходное количество признаков:  103
Количество не коррелируемых признаков:  27
Отношение коррелируемых исходному количеству признаков (сила корреляции):  0.738


In [996]:
# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']
# сформируем данные для проверики модели
# сформируем данные для анализа сбалансированности обучающих данных
X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()
y_train = pd.read_csv('target/target_train.csv')['flag']
X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()
y_valid = pd.read_csv('target/target_valid.csv')['flag']

In [997]:
# посмотрим на структуру данных в X_train_balanced
X_train_balanced.head(4)

f1    f2      f3      f4      f5      f6      f7   f8     f9  f10  \
id                                                                             
2335465  17.0  15.0  14.235  12.550  12.550  15.938  14.235  0.0  4.180  1.0   
390270    6.0  16.0  12.333   0.000   0.000  15.784  12.333  0.0  5.793  0.0   
2494034  14.0  13.0  12.500  11.422  11.422  15.822  12.500  0.0  4.355  3.0   
2018674  15.0   7.0  14.933  14.748  14.748  15.902  14.933  0.0  2.112  9.0   

         ...   f94  f95  f96  f97  f98  f99  f100  f101   f102  f103  
id       ...                                                          
2335465  ...  0.00  1.0  1.0  1.0  1.0  1.0   1.0  1.00  0.000   1.0  
390270   ...  0.00  1.0  1.0  1.0  1.0  1.0   1.0  1.00  0.000   1.0  
2494034  ...  0.35  0.0  1.0  1.0  1.0  1.0   1.0  0.86  0.132   0.5  
2018674  ...  0.34  0.0  1.0  1.0  1.0  1.0   1.0  0.87  0.124   0.5  

[4 rows x 103 columns]

In [998]:
# посмотрим на структуру данных в y_train_balanced
y_train_balanced.head(4)

id
2335465    1
390270     1
2494034    1
2018674    1
Name: flag, dtype: int64

In [999]:
# проверим что выборки действительно совпадают по id
X_train_balanced.index.to_list() == y_train_balanced.index.to_list()

True

##### <span style="color:MediumSlateBlue">Baseline обучение модели Hist Gradient Boosting Classifier</span>

In [1000]:
# обучаем модель Gradient Boosting Classifier
gradient_boosting = HistGradientBoostingClassifier(random_state=42)
gradient_boosting.fit(X_train_balanced[list_ncorr_features],y_train_balanced)

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_rf__pred_proba = gradient_boosting.predict_proba(X_train[list_ncorr_features])[:,1]
y_valid_rf_pred_proba = gradient_boosting.predict_proba(X_valid[list_ncorr_features])[:,1]

# Делаем предсказание для валидационной выборки
y_valid_rf_pred = gradient_boosting.predict(X_valid[list_ncorr_features])

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_rf__pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_rf_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_rf_pred))

# time: 30s

ROC AUC на обучающем наборе 0.657
ROC AUC на валидационном наборе 0.644
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.98      0.59      0.74     68747
           1       0.05      0.62      0.10      2503

    accuracy                           0.59     71250
   macro avg       0.51      0.60      0.42     71250
weighted avg       0.94      0.59      0.71     71250



##### <span style="color:MediumSlateBlue">Подбор гиперпараметров модели</span>

In [1762]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'relative'
count_features = dict_spaces[feature_space]

# для работы функции corr_transform_to_force
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()

# настроим оптимизацию гипер параметров
def optuna_hgbc(trial):
  # задаем пространства поиска гиперпараметров
  learning_rate = trial.suggest_float('learning_rate',0.01,0.1)
  max_iter = trial.suggest_int('max_iter', 150, 250,step = 1)
  max_leaf_nodes = trial.suggest_int('max_leaf_nodes', 2, 60,step = 1)
  max_depth = trial.suggest_int('max_depth', 1, 10,step = 1)
  min_samples_leaf = trial.suggest_int('min_samples_leaf', 1, 60,step = 1)
  max_features = trial.suggest_float('max_features',0.6,1)
  l2_regularization = trial.suggest_float('l2_regularization',0.01,1)
  class_0_weight = trial.suggest_float('class_0_weight',0.01,1)
  class_1_weight = trial.suggest_float('class_1_weight',0.5,1)
  threshold = trial.suggest_float('threshold',0.7,1)
  class_1_percent = trial.suggest_float('class_1_percent',0.01,0.25)
  random_state = trial.suggest_int('random_state', 1, 1000000)

  # создаем модель
  optuna_gradient_boosting = HistGradientBoostingClassifier(
      learning_rate= learning_rate,
      max_iter = max_iter,
      max_leaf_nodes =max_leaf_nodes,
      max_depth = max_depth,
      min_samples_leaf = min_samples_leaf,
      max_features=max_features,
      l2_regularization = l2_regularization,
      class_weight={0:class_0_weight,1:class_1_weight},
      random_state=42)

  # с помощью функции corr_transform_to_force получим
  # список не коррелируемых признаков
  list_ncorr_features = corr_transform_to_force(corr_matrix,threshold=threshold)[1]

  # сформируем данные для анализа сбалансированности обучающих данных
  X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
  y_train_pd = pd.read_csv('target/target_train.csv')

  # поготовим данные y_train_pd к работе с функцией class_1_percent_samples
  y_train_pd.set_index('id',drop=False,inplace=True)

  # подготовим данные для обучения модели
  # с помощью функции class_1_percent_samples зададим долю 
  # класса 1
  list_c1_percent_id = class_1_percent_samples(y_train_pd,class_1_percent,random_state=random_state)[:1000000]

  # подготовим данные для обучения
  X_train_balanced = X_train_pd.loc[list_c1_percent_id]
  y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']

  # освободим память от "тяжелых" и ненужных файлов
  del X_train_pd, y_train_pd
  gc.collect()

  # я не воспользовался параметром timeout метода optimize потому, что  
  # optimize отставливает поиск параметров, если время обучения 
  # превышает timeout. Мне нужно чтобы поиск параметров продолжился.
  try:
    # для модуля func_time_out упакуем обучение модели в функцию try_func
    def try_func():
            return optuna_gradient_boosting.fit(X_train_balanced,y_train_balanced)
    # обучаем модель с ограничением по времени 10 минут (600 секунд)
    optuna_gradient_boosting = func_timeout.func_timeout(600, try_func)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train_balanced, y_train_balanced
    gc.collect()

        # загружаем тестовые наборы
    # сформируем данные для анализа сбалансированности обучающих данных
    X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
    X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()[list_ncorr_features]
    y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
    y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()
    
    # делаем предсказание на обучающем и валидационном наборе и считаем метрики
    roc_train = metrics.roc_auc_score(y_train, optuna_gradient_boosting.predict_proba(X_train)[:,1])
    roc_valid = metrics.roc_auc_score(y_valid, optuna_gradient_boosting.predict_proba(X_valid)[:,1])
    f1_score = metrics.f1_score(y_valid, optuna_gradient_boosting.predict(X_valid))
    recall_1 = metrics.recall_score(y_valid, optuna_gradient_boosting.predict(X_valid),average=None,zero_division=0)[1]
    precision_1 = metrics.precision_score(y_valid, optuna_gradient_boosting.predict(X_valid),average=None,zero_division=0)[1]


    # удаляем крупные файлы чтобы высвободить память 
    del X_train, X_valid, y_train, y_valid
    gc.collect()

  except func_timeout.FunctionTimedOut:
    # удаляем крупные файлы чтобы высвободить память 
    del X_train_balanced, y_train_balanced
    gc.collect()
    
    # фиксируем пустые значения метрик
    roc_train = 0
    roc_valid = 0
    f1_score = 0
    recall_1 = 0
    precision_1 = 0
    pass

  return roc_train, roc_valid, f1_score, recall_1, precision_1

In [1763]:
# cоздаем объект исследования
# чтобы модель не переобучалась минимизируем roc_train 
# и максимизируем roc_valid
optuna_study_hgbc = optuna.create_study(study_name='HistGradientBoostingClassifier_'+feature_space+'_stat', 
                               directions=['maximize','maximize','maximize','maximize','maximize'], 
                               sampler=optuna.samplers.TPESampler(),
                               pruner='Hyperband',
                               storage='sqlite:///optuna_studies.db',
                               load_if_exists=True)

# ну случай удаления обучения
# optuna.delete_study(study_name='HistGradientBoostingClassifier'+feature_space+'_stat', storage='sqlite:///optuna_studies.db')

[I 2025-04-19 14:56:52,019] Using an existing study with name 'HistGradientBoostingClassifier_relative_stat' instead of creating a new one.


In [1003]:
# ищем лучшую комбинацию гиперпараметров n_trials раз
optuna_study_hgbc.optimize(optuna_hgbc, n_trials=300)

[I 2025-04-18 04:11:31,469] Trial 0 finished with values: [0.6116022835140923, 0.6163954789592213, 0.0, 0.0, 0.0] and parameters: {'learning_rate': 0.017482242691520235, 'max_iter': 187, 'max_leaf_nodes': 2, 'max_depth': 10, 'min_samples_leaf': 42, 'max_features': 0.8905887780382941, 'l2_regularization': 0.9656612822343854, 'class_0_weight': 0.6610413989942958, 'class_1_weight': 0.5686838644908798, 'threshold': 0.8255102913688669, 'class_1_percent': 0.22373491094169995, 'random_state': 809587}.
[I 2025-04-18 04:11:39,598] Trial 1 finished with values: [0.67718108853488, 0.6606099503584337, 0.015915119363395226, 0.008389932081502197, 0.15441176470588236] and parameters: {'learning_rate': 0.09758969800434612, 'max_iter': 219, 'max_leaf_nodes': 42, 'max_depth': 8, 'min_samples_leaf': 2, 'max_features': 0.6868563619533707, 'l2_regularization': 0.9936658525791845, 'class_0_weight': 0.23481969423514967, 'class_1_weight': 0.7635241014878849, 'threshold': 0.9217951963056893, 'class_1_percent':

In [1764]:
# из полученного результат соврмируем Data Frame
optuna_study_hgbc_pd = optuna_study_hgbc.trials_dataframe()
# переименуем столбы
optuna_study_hgbc_pd.rename(columns={
    'values_0': 'roc_train',
    'values_1': 'roc_valid',
    'values_2': 'f1_score',
    'values_3': 'recall_1',
    'values_4': 'precision_1'
},inplace=True)
optuna_study_hgbc_pd.tail(5)

number  roc_train  roc_valid  f1_score  recall_1  precision_1  \
295     295   0.679525   0.660987  0.088889  0.078306     0.102779   
296     296   0.681184   0.660956  0.000000  0.000000     0.000000   
297     297   0.680891   0.661799  0.115643  0.440671     0.066554   
298     298   0.686563   0.660436  0.103631  0.612865     0.056601   
299     299   0.686875   0.660134  0.012967  0.006792     0.142857   

                datetime_start          datetime_complete  \
295 2025-04-18 04:56:47.174287 2025-04-18 04:56:59.530931   
296 2025-04-18 04:56:59.537242 2025-04-18 04:57:16.005500   
297 2025-04-18 04:57:16.010509 2025-04-18 04:57:26.964556   
298 2025-04-18 04:57:26.969807 2025-04-18 04:57:39.430875   
299 2025-04-18 04:57:39.437180 2025-04-18 04:58:01.761555   

                  duration  params_class_0_weight  ...  \
295 0 days 00:00:12.356644               0.257270  ...   
296 0 days 00:00:16.468258               0.928635  ...   
297 0 days 00:00:10.954047               0.156316  ...   
298 0 days 00:00:12.461068               0.089407  ...   
299 0 days 00:00:22.324375               0.089690  ...   

     params_l2_regularization  params_learning_rate  params_max_depth  \
295                  0.512248              0.056141                 8   
296                  0.478046              0.031143                10   
297                  0.904618              0.087961                 7   
298                  0.162500              0.074545                 8   
299                  0.762569              0.075190                 8   

     params_max_features  params_max_iter  params_max_leaf_nodes  \
295             0.703002              244                     47   
296             0.770113              185                     53   
297             0.832519              160                     45   
298             0.754723              177                     44   
299             0.835145              157                     45   

     params_min_samples_leaf  params_random_state  params_threshold     state  
295                       26               262327          0.988041  COMPLETE  
296                       25               369580          0.983613  COMPLETE  
297                       28               341196          0.994317  COMPLETE  
298                       24               292404          0.972080  COMPLETE  
299                       24               322673          0.995306  COMPLETE  

[5 rows x 22 columns]

In [1765]:
# покаждем статистику обучения
print('Максимальное значение метрики ROC AUC на валидационном наборе:',round(optuna_study_hgbc_pd['roc_valid'].max(),3))
print('Среднее значение метрики ROC AUC на валидационном наборе:',round(optuna_study_hgbc_pd['roc_valid'].mean(),3))
print('Максимальное значение метрики f1_score на валидационном наборе:',round(optuna_study_hgbc_pd['f1_score'].max(),3))
print('Среднее значение метрики f1_score на валидационном наборе:',round(optuna_study_hgbc_pd['f1_score'].mean(),3))
print('Максимальное значение метрики recall_1 на валидационном наборе:',round(optuna_study_hgbc_pd['recall_1'].max(),3))
print('Среднее значение метрики recall_1 на валидационном наборе:',round(optuna_study_hgbc_pd['recall_1'].mean(),3))
print('Максимальное значение метрики precision_1 на валидационном наборе:',round(optuna_study_hgbc_pd['precision_1'].max(),3))
print('Среднее значение метрики precision_1 на валидационном наборе:',round(optuna_study_hgbc_pd['precision_1'].mean(),3))

Максимальное значение метрики ROC AUC на валидационном наборе: 0.664
Среднее значение метрики ROC AUC на валидационном наборе: 0.659
Максимальное значение метрики f1_score на валидационном наборе: 0.12
Среднее значение метрики f1_score на валидационном наборе: 0.084
Максимальное значение метрики recall_1 на валидационном наборе: 1.0
Среднее значение метрики recall_1 на валидационном наборе: 0.385
Максимальное значение метрики precision_1 на валидационном наборе: 0.5
Среднее значение метрики precision_1 на валидационном наборе: 0.081


In [1769]:
# Построим зависимость метрик качества модели от number

fig = px.scatter(
    data_frame=optuna_study_hgbc_pd[(optuna_study_hgbc_pd['roc_valid']>0.999*optuna_study_hgbc_pd['roc_valid'].max())],
    x='number', #ось абсцисс
    y=['roc_train','roc_valid','recall_1','precision_1','f1_score'], #ось ординат
)
fig.update_layout(
    title ={
        'text':'Зависимость качества модели от trials optuna', # Имя рабочей плоскости
        'font':{'size':35,'family':"Times New Roman"}, # размер и стиль написания имени рабочей плоскости
        'x':0.5, # Смешение имени по оси "x" на половину рабочей плоскости
        },
    height =800,# Высота рабочей плоскости
    width = 1350, # Ширина рабочей плоскости
    bargap=0.2, # Добавил расстояния между столбами гистограммы
    xaxis_title='trials optuna',
    yaxis_title='Величина параметра')
fig.update_xaxes(showspikes=True)
fig.update_yaxes(showspikes=True)

fig.show()

<span style="color:Blue">

Вывод:  

Их всех выбираем точку $number =158$.   
В этой точке оптимальные значения метрик $recall_1$ и $precision_1$, а  
также относительно высокая метрика $ROC AUC$.   
Посмотрим каким значениям гиперпараметров соотвествует выбранная точка.

In [1770]:
# определим номер лучшге варианта
best_optuna_number = 158

# сформируем словарь лучших гипирпарметров HistGradientBoostingClassifier
best_param_hgbc = {
    'learning_rate' : optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_learning_rate'].iloc[0],
    'max_iter' : optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_max_iter'].iloc[0],
    'max_leaf_nodes' : optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_max_leaf_nodes'].iloc[0],
    'max_depth' : optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_max_depth'].iloc[0],
    'min_samples_leaf' : optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_min_samples_leaf'].iloc[0],
    'max_features' : optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_max_features'].iloc[0],
    'l2_regularization' : optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_l2_regularization'].iloc[0],
    'class_weight' : {0: optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_class_0_weight'].iloc[0],
                      1: optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_class_1_weight'].iloc[0],}
    }

# определим перменные для лучших значений параметров
best_threshold = optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_threshold'].iloc[0]
best_class_1_percent = optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_class_1_percent'].iloc[0]
best_random_state = optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_random_state'].iloc[0]


# Выведем принятые наилучшие параметры
print('best learning rate:',round(best_param_hgbc['learning_rate'],3))
print('best max iter:',best_param_hgbc['max_iter'])
print('best max leaf nodes:',best_param_hgbc['max_leaf_nodes'])
print('best max depth:',best_param_hgbc['max_depth'])
print('best min samples leaf:',best_param_hgbc['min_samples_leaf'])
print('best max features:',round(best_param_hgbc['max_features'],3))
print('best l2 regularization:',round(best_param_hgbc['l2_regularization'],3))
print('best class 0 weight:',round(best_param_hgbc['class_weight'][0],3))
print('best class 1 weight:',round(best_param_hgbc['class_weight'][1],3))

print('best class 1 percent:',round(best_class_1_percent,3))
print('best threshold:',round(best_threshold,3))
print('time for best train:',round(optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['duration'].iloc[0].seconds/60),'minutes')

print()
print('ROC AUC на обучающем наборе:', round(optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['roc_train'].iloc[0],3))
print('ROC AUC на валидационном наборе:', round(optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['roc_valid'].iloc[0],3))
print('precision класса 1:', round(optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['precision_1'].iloc[0],3))
print('recall класса 1:', round(optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['recall_1'].iloc[0],3))

best learning rate: 0.069
best max iter: 219
best max leaf nodes: 26
best max depth: 8
best min samples leaf: 14
best max features: 0.786
best l2 regularization: 0.479
best class 0 weight: 0.278
best class 1 weight: 0.924
best class 1 percent: 0.192
best threshold: 0.922
time for best train: 0 minutes

ROC AUC на обучающем наборе: 0.672
ROC AUC на валидационном наборе: 0.663
precision класса 1: 0.066
recall класса 1: 0.438


##### <span style="color:MediumSlateBlue">Обучение модели с лучшими параметрами</span>

In [1771]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'relative'
count_features = dict_spaces[feature_space]

# для работы функции corr_transform_to_force
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()

# с помощью функции corr_transform_to_force получим
# список не коррелируемых признаков
list_ncorr_features = corr_transform_to_force(corr_matrix,threshold=best_threshold)[1]

# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
y_train_pd = pd.read_csv('target/target_train.csv')

# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)

# подготовим данные для обучения модели
# с помощью функции class_1_percent_samples зададим долю 
# класса 1
list_c1_percent_id = class_1_percent_samples(y_train_pd,best_class_1_percent,random_state=best_random_state)[:1000000]

# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']

# освободим память от "тяжелых" и ненужных файлов
del X_train_pd, y_train_pd
gc.collect()

# обучаем модель HistGradientBoostingClassifier с наилучшеми параметрами
gradient_boosting = HistGradientBoostingClassifier(
        **best_param_hgbc,
        random_state=42)
gradient_boosting.fit(X_train_balanced,y_train_balanced)

# удаляем крупные файлы чтобы высвободить память 
del X_train_balanced, y_train_balanced
gc.collect()

# сформируем данные для анализа сбалансированности обучающих данных
X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()[list_ncorr_features]
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

# делаем предсказание на обучающем и валидационном наборе и считаем метрики
y_train_gb_pred_proba = gradient_boosting.predict_proba(X_train)[:,1]
y_valid_gb_pred_proba = gradient_boosting.predict_proba(X_valid)[:,1]
y_valid_gb_pred = gradient_boosting.predict(X_valid)

# удаляем крупные файлы чтобы высвободить память 
del X_train, X_valid
gc.collect()

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_gb_pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_gb_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_gb_pred,zero_division=0))

# time: 1m 40s

ROC AUC на обучающем наборе 0.672
ROC AUC на валидационном наборе 0.663
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.97      0.78      0.86     68747
           1       0.07      0.44      0.11      2503

    accuracy                           0.76     71250
   macro avg       0.52      0.61      0.49     71250
weighted avg       0.94      0.76      0.84     71250



### <span style="color:RoyalBlue">Построение модели на сбалансированных данных подпрострнства payments stat</span>

#### <span style="color:MediumBlue">Построение модели Logistic Regression</span>

##### <span style="color:MediumSlateBlue">Формирование данных для обучения</span>

Анализ исходных данных, в частности target, показал что представленные данные   
имееют перекос: 96% клиентов у которых не случился дефолт (flag = 0),    
против 4 % - для которых произошел дефолт (flag = 1).  
С помощью функции class_1_percent_samples, сформируем сбаланисрованную выборку  
для обучения моделей.
За основу сбалансировных данных возьмем данные клиентов с дефолтом  
и к ним будем добирать необходимое количество клиентов до сбалансированности. 


Функция class_1_percent_samples принемает две переменные:
- target_data - массив с id и целевой переменной
- class_1_percent - процент класса 1 в результирующем массиве

In [1022]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'payments'
count_features = dict_spaces[feature_space]

In [1023]:
# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

In [1024]:
# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)
y_train_pd.head(4)

id  flag
id                    
1825800  1825800     0
2166483  2166483     0
2534345  2534345     0
1803283  1803283     0

In [1025]:
# взглянем на сблансиорованность данных в y_train
y_train_pd['flag'].value_counts(normalize=True)

flag
0    0.964242
1    0.035758
Name: proportion, dtype: float64

In [1026]:
# сбалансируем данные в y_train_pd
list_c1_percent_id = class_1_percent_samples(y_train_pd,0.5)
# list_c1_percent_features - список 'id' из y_train_pd соотвествующих  
# заданному проценту класса 1
len(list_c1_percent_id)

45860

In [1027]:
# проверим сбалансированность полученного y_train
y_train_pd.loc[list_c1_percent_id]['flag'].value_counts(normalize=True)

flag
1    0.5
0    0.5
Name: proportion, dtype: float64

В отличие от данных в *transform_data_torow*, где модели показываеются последние N  
операций клиента, в данные в *transform_data_stat* сфомированы из различных статистических   
характеристик ряда определяющего клиентскую историю в банке. 

Соотвественно, если в данных *transform_data_torow* была сильная корреляция между признаками,  
то я не смог бы ее убрать, иначе потярется смысл "показать последовательный ряд в историии клиента".  
Признаки в *transform_data_stat* не имеют такой особенности. Поэтому, необходимо проанализировать  
данные в *transform_data_stat* и, в случае сильной коррреляции признаков, устранить ее.

In [1028]:
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()
corr_matrix.shape

(426, 426)

In [1029]:
# с помощью функции corr_transrom_to_power получим
# силу корреляции матрицы и список не коррелируемых признаков

# для начального анализа зададим порог силы корреляции, при котором признаки 
# будут отнесены к "сильно скоррелированными" равным 0.6
ncorr_matrix,list_ncorr_features,corr_power =corr_transform_to_force(corr_matrix,threshold=0.6)

# Выведем результаты преобразования
print('Исходное количество признаков: ', corr_matrix.shape[0])
print('Количество не коррелируемых признаков: ', len(list_ncorr_features))
# сила корреляции признаков
print('Отношение коррелируемых исходному количеству признаков (сила корреляции): ',corr_power)

Исходное количество признаков:  426
Количество не коррелируемых признаков:  54
Отношение коррелируемых исходному количеству признаков (сила корреляции):  0.873


In [1030]:
# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']
# сформируем данные для проверики модели
# сформируем данные для анализа сбалансированности обучающих данных
X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()
y_train = pd.read_csv('target/target_train.csv')['flag']
X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()
y_valid = pd.read_csv('target/target_valid.csv')['flag']

In [1031]:
# посмотрим на структуру данных в X_train_balanced
X_train_balanced.head(4)

f1   f2     f3   f4   f5     f6     f7   f8     f9  f10  ...  \
id                                                                  ...   
2335465  17.0  3.0  0.294  0.0  0.0  2.835  0.294  0.0  0.749  0.0  ...   
390270    6.0  3.0  0.500  0.0  0.0  2.894  0.500  0.0  1.118  0.0  ...   
2494034  14.0  3.0  0.214  0.0  0.0  2.846  0.214  0.0  0.773  0.0  ...   
2018674  15.0  3.0  0.200  0.0  0.0  2.842  0.200  0.0  0.748  0.0  ...   

          f417  f418  f419  f420  f421  f422  f423  f424   f425  f426  
id                                                                     
2335465  1.273   1.0   1.6   4.0   4.0   4.0   4.0  0.76  1.721   2.5  
390270   0.000   4.0   4.0   4.0   4.0   4.0   4.0  1.00  0.000   4.0  
2494034  0.000   4.0   4.0   4.0   4.0   4.0   4.0  1.00  0.000   4.0  
2018674  1.200   1.0   3.4   4.0   4.0   4.0   4.0  0.80  1.543   2.5  

[4 rows x 426 columns]

In [1032]:
# посмотрим на структуру данных в y_train_balanced
y_train_balanced.head(4)

id
2335465    1
390270     1
2494034    1
2018674    1
Name: flag, dtype: int64

In [1033]:
# проверим что выборки действительно совпадают по id
X_train_balanced.index.to_list() == y_train_balanced.index.to_list()

True

##### <span style="color:MediumSlateBlue">Baseline обучение модели LogisticRegression</span>

In [1034]:
# обучаем модель логистической регрессии
logistic_regression = linear_model.LogisticRegression(random_state=42, max_iter=10000)
logistic_regression.fit(X_train_balanced[list_ncorr_features],y_train_balanced)

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_LR_pred_proba = logistic_regression.predict_proba(X_train[list_ncorr_features])[:,1]
y_valid_LR_pred_proba = logistic_regression.predict_proba(X_valid[list_ncorr_features])[:,1]

# Делаем предсказание для валидационной выборки
y_valid_LR_pred = logistic_regression.predict(X_valid[list_ncorr_features])

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_LR_pred_proba),3))
print('ROC AUC на тестовом наборе', round(metrics.roc_auc_score(y_valid, y_valid_LR_pred_proba),3))

print('Основные метрики на тестовом наборе:')
print(metrics.classification_report(y_valid,y_valid_LR_pred))

# time: 3m 5s

ROC AUC на обучающем наборе 0.652
ROC AUC на тестовом наборе 0.645
Основные метрики на тестовом наборе:
              precision    recall  f1-score   support

           0       0.97      0.70      0.81     68747
           1       0.06      0.50      0.10      2503

    accuracy                           0.69     71250
   macro avg       0.52      0.60      0.46     71250
weighted avg       0.94      0.69      0.79     71250



##### <span style="color:MediumSlateBlue">Анализ влияния scaler преобразования на качество и скорость схождения модели</span>

In [1035]:
# формируем список из необходимых scaler
scalers = [MinMaxScaler(),RobustScaler() ,StandardScaler()]

# сформируем списко для заполнения данными результатов анализа
scalers_data = []

# установим ограничение на время обучения модели в 600 секунд (10 минут)
time_out = 600

for scaler in scalers:
        # для того чтобы следить за выполнением цикла введем индикатор
        print('current scaler: ', scaler)

         # сформируем список для заполнения данными текушего scaler
        current_scaler_data = [scaler]
        
        # выполним scaler преобразование
        X_train_s_balanced = scaler.fit_transform(X_train_balanced[list_ncorr_features])
        X_train_s = scaler.transform(X_train[list_ncorr_features])
        X_valid_s = scaler.transform(X_valid[list_ncorr_features])

        try:
                # для модуля func_time_out упакуем обучение модели в функцию try_func
                def try_func():
                        logistic_regression = linear_model.LogisticRegression(random_state=42, max_iter=10000)
                        return logistic_regression.fit(X_train_s_balanced,y_train_balanced)
                    
                # фиксируем время начала
                start_time = time.time()
                
                # запускаем обучение модели с ограничением по времени
                logistic_regression = func_timeout.func_timeout(time_out, try_func)
                
                # фиксируем время окончания обучения
                end_time = time.time()
                
                # запишем время обучения модели
                current_scaler_data.append(round(end_time-start_time))

                # Делаем предсказание для обучающей и валидационной выборки
                y_valid_lr_pred = logistic_regression.predict(X_valid_s)
                
                # для метрик ROC AUC делаем предсказание модели для обучающей и валидационной выборки  
                # в виде вероятности принадлежности к классу 1 
                y_train_lr_pred_proba = logistic_regression.predict_proba(X_train_s)[:,1]
                y_valid_lr_pred_proba = logistic_regression.predict_proba(X_valid_s)[:,1]

                #Считаем метрики ROC AUC yна обуающем и валидационном наборе и добавляем их в спискок
                current_scaler_data.append(round(metrics.roc_auc_score(y_train, y_train_lr_pred_proba),3))
                current_scaler_data.append(round(metrics.roc_auc_score(y_valid, y_valid_lr_pred_proba),3))

                #Считаем метрики для класса 0 на валидационном наборе и добавляем их в список
                current_scaler_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))
                current_scaler_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))


                #Считаем метрики для класса 1 на валидационном набопе и добавляем их в список
                current_scaler_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))
                current_scaler_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))

                # добавляем полученные данные в список scalers_data
                scalers_data.append(current_scaler_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                scaler_pd =pd.DataFrame(
                        columns=['scaler','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = scalers_data)
                # сохраняем dataframe
                scaler_pd.to_csv('data_recovery/scaler_pd.csv',index=False)
               
                # очистим output от прошедшей итерации
                clear_output()

        except func_timeout.FunctionTimedOut:
                # если время обучения привышает лимит
                # запишем в current_scaler_data соотвествующую данные
                current_scaler_data = [scaler,'>30m',0,0,0,0,0,0]
                # добавляем полученные данные в список scalers_data
                scalers_data.append(current_scaler_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                scaler_pd =pd.DataFrame(
                        columns=['scaler','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = scalers_data)
                # сохраняем dataframe
                scaler_pd.to_csv('data_recovery/scaler_pd.csv',index=False)
                
                # очистим output от прошедшей итерации
                clear_output()
                # переходим к следующему scaler
                pass
# очистим output
clear_output()

# сформируем данные соотвествующие лучщему ROC AUC на валидацинном наборе
best_roc_valid_data = scaler_pd[scaler_pd['roc_valid']==scaler_pd['roc_valid'].max()]

# выведем лучший результат на валидационном наборе
print('result:')
print('best scaler on valid:',best_roc_valid_data.iloc[0]['scaler'])
print('ROC AUC on train:', best_roc_valid_data.iloc[0]['roc_train'])
print('ROC AUC on valid:', best_roc_valid_data.iloc[0]['roc_valid'])
print('Time fit for best scaler:', best_roc_valid_data.iloc[0]['time_fit'],' seconds')

# выведем полученный dataframe
scaler_pd

# time: 

result:
best scaler on valid: MinMaxScaler()
ROC AUC on train: 0.652
ROC AUC on valid: 0.645
Time fit for best scaler: 0  seconds


scaler  time_fit  roc_train  roc_valid  recall_0  precision_0  \
0    MinMaxScaler()         0      0.652      0.645     0.698        0.975   
1    RobustScaler()         0      0.652      0.645     0.698        0.975   
2  StandardScaler()         0      0.652      0.645     0.698        0.975   

   recall_1  precision_1  
0     0.504        0.057  
1     0.504        0.057  
2     0.503        0.057

##### <span style="color:MediumSlateBlue"> Анализ влияния solver оптимизатора на качество и скорость обучения модели</span>

Проверим качество и скорость сходимости модели при разных solver  
Проверку осуществим через цикл  
Чтобы модель не сходилась бесконечно с помощью модуля func_timeout  
поставим ограничение времени схождения в 10 минут

In [1036]:
# подготовим данные для обучения модели

# обьявим scaler
scaler = StandardScaler()
# выполним scaler преобразование
X_train_s_balanced = scaler.fit_transform(X_train_balanced[list_ncorr_features])
X_train_s = scaler.transform(X_train[list_ncorr_features])
X_valid_s = scaler.transform(X_valid[list_ncorr_features])

# time: 10s

In [1037]:
# Зададим список solvers
solvers_list = ['lbfgs', 'liblinear', 'newton-cg', 'newton-cholesky', 'sag', 'saga']

# сформируем список для заполнения
solvers_data = []

# установим ограничение на время обучения модели в 180 секунд (3 минут)
time_out = 180

for solver in solvers_list:
        # для того чтобы следить за выполнением цикла введем индикатор
        print('current solver: ', solver)

         # сформируем список для заполнения данными текушего solver
        current_solver_data = [solver]
        
        try:
                # для модуля func_time_out упакуем обучение модели в функцию try_func
                def try_func():
                        logistic_regression = linear_model.LogisticRegression(solver= solver,
                                                                  random_state=42, 
                                                                  max_iter=10000)
                        return logistic_regression.fit(X_train_s_balanced,y_train_balanced)
                    
                # фиксируем время начала
                start_time = time.time()
                
                # запускаем обучение модели с ограничением по времени
                logistic_regression = func_timeout.func_timeout(time_out, try_func)
                
                # фиксируем время окончания обучения
                end_time = time.time()
                
                # запишем время обучения модели
                current_solver_data.append(round(end_time-start_time))

                # Делаем предсказание для обучающей и валидационной выборки
                y_valid_lr_pred = logistic_regression.predict(X_valid_s)
                
                # для метрик ROC AUC делаем предсказание модели для обучающей и валидационной выборки  
                # в виде вероятности принадлежности к классу 1 
                y_train_lr_pred_proba = logistic_regression.predict_proba(X_train_s)[:,1]
                y_valid_lr_pred_proba = logistic_regression.predict_proba(X_valid_s)[:,1]

                #Считаем метрики ROC AUC yна обуающем и валидационном наборе и добавляем их в спискок
                current_solver_data.append(round(metrics.roc_auc_score(y_train, y_train_lr_pred_proba),3))
                current_solver_data.append(round(metrics.roc_auc_score(y_valid, y_valid_lr_pred_proba),3))

                #Считаем метрики для класса 0 на валидационном наборе и добавляем их в список
                current_solver_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))
                current_solver_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))


                #Считаем метрики для класса 1 на валидационном набопе и добавляем их в список
                current_solver_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))
                current_solver_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))

                # запишем данные полученные на одной итерации
                solvers_data.append(current_solver_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                solvers_pd =pd.DataFrame(
                        columns=['solver','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = solvers_data)
                # сохраняем dataframe
                solvers_pd.to_csv('data_recovery/solvers_pd.csv',index=False)
               
                # очистим output от прошедшей итерации
                clear_output()

        except func_timeout.FunctionTimedOut:
                # если время обучения привышает лимит
                # запишем в current_solver_data соотвествующую данные
                current_solver_data = [solver,'>3m',0,0,0,0,0,0]
                # добавляем полученные данные в список solvers_data
                solvers_data.append(current_solver_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                solvers_pd =pd.DataFrame(
                        columns=['solver','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = solvers_data)
                # сохраняем dataframe
                solvers_pd.to_csv('data_recovery/solvers_pd.csv',index=False)
                
                # очистим output от прошедшей итерации
                clear_output()
                # переходим к следующему solver
                pass
# очистим output
clear_output()

# сформируем данные соотвествующие лучщему ROC AUC на валидацинном наборе
best_roc_valid_data = solvers_pd[solvers_pd['roc_valid']==solvers_pd['roc_valid'].max()]

# выведем лучший результат на валидационном наборе
print('result:')
print('best solver on valid:',best_roc_valid_data.iloc[0]['solver'])
print('ROC AUC on train:', best_roc_valid_data.iloc[0]['roc_train'])
print('ROC AUC on valid:', best_roc_valid_data.iloc[0]['roc_valid'])
print('Time fit for best solver:', best_roc_valid_data.iloc[0]['time_fit'],' seconds')

# выведем полученный dataframe
solvers_pd

# time: 2m 35s

result:
best solver on valid: lbfgs
ROC AUC on train: 0.652
ROC AUC on valid: 0.645
Time fit for best solver: 0  seconds


solver  time_fit  roc_train  roc_valid  recall_0  precision_0  \
0            lbfgs         0      0.652      0.645     0.698        0.975   
1        liblinear         0      0.652      0.645     0.698        0.975   
2        newton-cg         0      0.652      0.645     0.698        0.975   
3  newton-cholesky         0      0.652      0.645     0.698        0.975   
4              sag         0      0.652      0.645     0.698        0.975   
5             saga         0      0.652      0.645     0.698        0.975   

   recall_1  precision_1  
0     0.503        0.057  
1     0.503        0.057  
2     0.503        0.057  
3     0.503        0.057  
4     0.503        0.057  
5     0.503        0.057

##### <span style="color:MediumSlateBlue">Подбор гиперпараметров модели</span>

In [1772]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'payments'
count_features = dict_spaces[feature_space]

# для работы функции corr_transform_to_force
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()

# для выбора sceler преобразвания нам понадобится словарь
dict_scalers ={
    'MinMaxScaler': MinMaxScaler(),
    'RobustScaler':RobustScaler(),
    'StandardScaler':StandardScaler()}

# настроим оптимизацию гипер параметров
def optuna_lg(trial):
  # задаем пространства поиска гиперпараметров
  solver = trial.suggest_categorical("solver", ['lbfgs', 'liblinear', 'newton-cg', 'newton-cholesky'])
  C = trial.suggest_float('C',0.01,1)
  class_0_weight = trial.suggest_float('class_0_weight',0.2,0.6)
  class_1_weight = trial.suggest_float('class_1_weight',0.2,0.6)
  threshold = trial.suggest_float('threshold',0.6,1)
  class_1_percent = trial.suggest_float('class_1_percent',0.01,0.3)
  scaler = trial.suggest_categorical("scaler", ['MinMaxScaler','RobustScaler','StandardScaler'])
  random_state = trial.suggest_int('random_state', 1, 1000000)


  # создаем модель
  optuna_log_reg = linear_model.LogisticRegression(
      solver=solver,
      C=C,
      class_weight={0:class_0_weight,1:class_1_weight},
      random_state=random_state,
      max_iter=10000)

  # с помощью функции corr_transform_to_force получим
  # список не коррелируемых признаков
  list_ncorr_features = corr_transform_to_force(corr_matrix,threshold=threshold)[1]

  # обьявим scaler
  scaler = dict_scalers[scaler]

  # сформируем данные для анализа сбалансированности обучающих данных
  X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
  y_train_pd = pd.read_csv('target/target_train.csv')

  # поготовим данные y_train_pd к работе с функцией class_1_percent_samples
  y_train_pd.set_index('id',drop=False,inplace=True)

  # подготовим данные для обучения модели
  # с помощью функции class_1_percent_samples зададим долю 
  # класса 1
  list_c1_percent_id = class_1_percent_samples(y_train_pd,class_1_percent,random_state=random_state)[:1000000]

  # подготовим данные для обучения
  X_train_s_balanced = scaler.fit_transform(X_train_pd.loc[list_c1_percent_id])
  y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

  # освободим память от "тяжелых" и ненужных файлов
  del X_train_pd, y_train_pd
  gc.collect()

  # я не воспользовался параметром timeout метода optimize потому, что  
  # optimize отставливает поиск параметров, если время обучения 
  # превышает timeout. Мне нужно чтобы поиск параметров продолжился.
  try:
    # для модуля func_time_out упакуем обучение модели в функцию try_func
    def try_func():
            return optuna_log_reg.fit(X_train_s_balanced, y_train_balanced)
    # обучаем модель с ограничением по времени 10 минут (600 секунд)
    optuna_log_reg = func_timeout.func_timeout(600, try_func)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train_s_balanced, y_train_balanced
    gc.collect()

    # загружаем тестовые наборы
    # сформируем данные для анализа сбалансированности обучающих данных
    X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
    X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()[list_ncorr_features]
    y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
    y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

    # подготовим данные для проверки модели
    X_train_s = scaler.transform(X_train)
    X_valid_s = scaler.transform(X_valid)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train, X_valid
    gc.collect()

    # делаем предсказание на обучающем и валидационном наборе и считаем метрики
    roc_train = metrics.roc_auc_score(y_train, optuna_log_reg.predict_proba(X_train_s)[:,1])
    roc_valid = metrics.roc_auc_score(y_valid, optuna_log_reg.predict_proba(X_valid_s)[:,1])
    f1_score = metrics.f1_score(y_valid, optuna_log_reg.predict(X_valid_s))
    recall_1 = metrics.recall_score(y_valid, optuna_log_reg.predict(X_valid_s),average=None,zero_division=0)[1]
    precision_1 = metrics.precision_score(y_valid, optuna_log_reg.predict(X_valid_s),average=None,zero_division=0)[1]

    # удаляем крупные файлы чтобы высвободить память 
    del X_train_s, X_valid_s, y_train, y_valid
    gc.collect()

  except func_timeout.FunctionTimedOut:
    # удаляем крупные файлы чтобы высвободить память 
    del X_train_s_balanced, y_train_balanced
    gc.collect()
    
    # фиксируем пустые значения метрик
    roc_train = 0
    roc_valid = 0
    f1_score = 0
    recall_1 = 0
    precision_1 = 0
    pass

  return roc_train, roc_valid, f1_score, recall_1, precision_1

In [1773]:
# cоздаем объект исследования
# чтобы модель не переобучалась минимизируем roc_train 
# и максимизируем roc_valid
optuna_study_lg = optuna.create_study(study_name='LogisticRegression_'+feature_space+'_stat', 
                               directions=['maximize','maximize','maximize','maximize','maximize'], 
                               sampler=optuna.samplers.TPESampler(),
                               pruner='Hyperband',
                               storage='sqlite:///optuna_studies.db',
                               load_if_exists=True)
# optuna.delete_study(study_name='LogisticRegression_'+feature_space+'_stat', storage='sqlite:///optuna_studies.db')

[I 2025-04-19 14:58:42,089] Using an existing study with name 'LogisticRegression_payments_stat' instead of creating a new one.


In [1040]:
# ищем лучшую комбинацию гиперпараметров n_trials раз
optuna_study_lg.optimize(optuna_lg, n_trials=300)

[I 2025-04-18 04:58:49,161] Trial 0 finished with values: [0.6593216132136277, 0.6557169609045694, 0.11985846970367094, 0.2165401518178186, 0.08286194771441675] and parameters: {'solver': 'lbfgs', 'C': 0.4559229157912227, 'class_0_weight': 0.21843929066248916, 'class_1_weight': 0.3230416677646334, 'threshold': 0.7974536401552528, 'class_1_percent': 0.2659562802935648, 'scaler': 'RobustScaler', 'random_state': 800752}.
[I 2025-04-18 04:59:03,391] Trial 1 finished with values: [0.6595657236351986, 0.6555396996918897, 0.0031570639305445935, 0.0015980823012385138, 0.12903225806451613] and parameters: {'solver': 'lbfgs', 'C': 0.7630579814173876, 'class_0_weight': 0.23118156254913283, 'class_1_weight': 0.5978063928605813, 'threshold': 0.8442152137651928, 'class_1_percent': 0.041237801199447664, 'scaler': 'MinMaxScaler', 'random_state': 306027}.
[I 2025-04-18 04:59:11,096] Trial 2 finished with values: [0.6547491618327721, 0.6516763676335717, 0.0345514950166113, 0.020775069916100678, 0.102564

In [1774]:
# из полученного результат соврмируем Data Frame
optuna_study_lg_pd = optuna_study_lg.trials_dataframe().dropna()
# переименуем столбы
optuna_study_lg_pd.rename(columns={
    'values_0': 'roc_train',
    'values_1': 'roc_valid',
    'values_2': 'f1_score',
    'values_3': 'recall_1',
    'values_4': 'precision_1'
},inplace=True)
# Выделим время потраченное на обучение модели
optuna_study_lg_pd.tail()

number  roc_train  roc_valid  f1_score  recall_1  precision_1  \
295     295   0.667028   0.660084  0.124210  0.333600     0.076311   
296     296   0.666905   0.659810  0.115101  0.146624     0.094734   
297     297   0.659371   0.655573  0.117564  0.198562     0.083501   
298     298   0.665159   0.660520  0.124370  0.221734     0.086422   
299     299   0.663376   0.658620  0.034002  0.019976     0.114155   

                datetime_start          datetime_complete  \
295 2025-04-18 06:01:10.902562 2025-04-18 06:01:32.331708   
296 2025-04-18 06:01:32.337222 2025-04-18 06:01:56.031898   
297 2025-04-18 06:01:56.037107 2025-04-18 06:02:05.738577   
298 2025-04-18 06:02:05.745103 2025-04-18 06:02:21.257348   
299 2025-04-18 06:02:21.262743 2025-04-18 06:02:37.089747   

                  duration  params_C  params_class_0_weight  \
295 0 days 00:00:21.429146  0.898159               0.292041   
296 0 days 00:00:23.694676  0.483267               0.420949   
297 0 days 00:00:09.701470  0.248715               0.290332   
298 0 days 00:00:15.512245  0.231041               0.286281   
299 0 days 00:00:15.827004  0.912899               0.255278   

     params_class_1_percent  params_class_1_weight  params_random_state  \
295                0.259244               0.559120               545519   
296                0.238404               0.556108               248478   
297                0.248133               0.447468               127707   
298                0.232575               0.494917               445460   
299                0.153727               0.320056               221656   

    params_scaler params_solver  params_threshold     state  
295  RobustScaler         lbfgs          0.983068  COMPLETE  
296  RobustScaler         lbfgs          0.986738  COMPLETE  
297  RobustScaler         lbfgs          0.807243  COMPLETE  
298  RobustScaler         lbfgs          0.949757  COMPLETE  
299  MinMaxScaler         lbfgs          0.936515  COMPLETE

In [1775]:
# покаждем статистику обучения
print('Максимальное значение метрики ROC AUC на валидационном наборе:',round(optuna_study_lg_pd['roc_valid'].max(),3))
print('Среднее значение метрики ROC AUC на валидационном наборе:',round(optuna_study_lg_pd['roc_valid'].mean(),3))
print('Максимальное значение метрики f1_score на валидационном наборе:',round(optuna_study_lg_pd['f1_score'].max(),3))
print('Среднее значение метрики f1_score на валидационном наборе:',round(optuna_study_lg_pd['f1_score'].mean(),3))
print('Максимальное значение метрики recall_1 на валидационном наборе:',round(optuna_study_lg_pd['recall_1'].max(),3))
print('Среднее значение метрики recall_1 на валидационном наборе:',round(optuna_study_lg_pd['recall_1'].mean(),3))
print('Максимальное значение метрики precision_1 на валидационном наборе:',round(optuna_study_lg_pd['precision_1'].max(),3))
print('Среднее значение метрики precision_1 на валидационном наборе:',round(optuna_study_lg_pd['precision_1'].mean(),3))

Максимальное значение метрики ROC AUC на валидационном наборе: 0.662
Среднее значение метрики ROC AUC на валидационном наборе: 0.658
Максимальное значение метрики f1_score на валидационном наборе: 0.129
Среднее значение метрики f1_score на валидационном наборе: 0.092
Максимальное значение метрики recall_1 на валидационном наборе: 0.611
Среднее значение метрики recall_1 на валидационном наборе: 0.199
Максимальное значение метрики precision_1 на валидационном наборе: 1.0
Среднее значение метрики precision_1 на валидационном наборе: 0.091


In [1781]:
# Визуализируем метрики полученные при optuna оптимизации
fig = px.scatter(
    data_frame=optuna_study_lg_pd[(optuna_study_lg_pd['roc_valid']>0.9999*optuna_study_lg_pd['roc_valid'].max())],
    x='number', #ось абсцисс
    y=['roc_train','roc_valid','recall_1','precision_1','f1_score'], #ось ординат
)
fig.update_layout(
    title ={
        'text':'Зависимость качества модели от trials optuna', # Имя рабочей плоскости
        'font':{'size':35,'family':"Times New Roman"}, # размер и стиль написания имени рабочей плоскости
        'x':0.5, # Смешение имени по оси "x" на половину рабочей плоскости
        },
    height =800,# Высота рабочей плоскости
    width = 1350, # Ширина рабочей плоскости
    bargap=0.2, # Добавил расстояния между столбами гистограммы
    xaxis_title='trials optuna',
    yaxis_title='Величина метрики')
fig.update_xaxes(showspikes=True)
fig.update_yaxes(showspikes=True)

fig.show()

<span style="color:Blue">

Вывод:  

Их всех выбираем точку $number =59$.   
В этой точке самые оптимальные значения $recall$ и $precision$.  
Посмотрим каким значениям гиперпараметров соотвествует выбранная точка.

In [1782]:
# определим номер лучшге варианта
best_optuna_number = 59

# сформируем словарь лучших гипирпарметров RandomForestClassifier
best_param_lr = {
    'solver' : optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_solver'].iloc[0],
    'C' : round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_C'].iloc[0],3),
    'class_weight' : {0:round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_class_0_weight'].iloc[0],3),
                      1:round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_class_1_weight'].iloc[0],3)},
    }

# создадим перменные
best_threshold = optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_threshold'].iloc[0]
best_scaler = optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_scaler'].iloc[0]
best_class_1_percent = optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_class_1_percent'].iloc[0]
best_random_state = optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_random_state'].iloc[0]

# Выведем принятые наилучшие праметры
print('best solver:',best_param_lr['solver'])
print('best C:',best_param_lr['C'])
print('best class 0 weight:',best_param_lr['class_weight'][0])
print('best class 1 weight:',best_param_lr['class_weight'][1])

print('best class 1 percent:',round(best_class_1_percent,3))
print('best scaler:',best_scaler)
print('best threshold:',round(best_threshold,3))
print('best best random state:',best_random_state)
print('time for best train:',round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['duration'].iloc[0].seconds/60),'minutes')

print()
print('ROC AUC на обучающем наборе:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['roc_train'].iloc[0],3))
print('ROC AUC на валидационном наборе:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['roc_valid'].iloc[0],3))
print('precision класса 1:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['precision_1'].iloc[0],3))
print('recall класса 1:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['recall_1'].iloc[0],3))


best solver: newton-cg
best C: 0.505
best class 0 weight: 0.347
best class 1 weight: 0.521
best class 1 percent: 0.14
best scaler: StandardScaler
best threshold: 0.945
best best random state: 382544
time for best train: 0 minutes

ROC AUC на обучающем наборе: 0.665
ROC AUC на валидационном наборе: 0.662
precision класса 1: 0.109
recall класса 1: 0.027


##### <span style="color:MediumSlateBlue">Обучение модели с лучшими параметрами</span>

In [1783]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'payments'
count_features = dict_spaces[feature_space]

# для работы функции corr_transform_to_force
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()

# подготовим данные
# для выбора sceler преобразвания нам понадобится словарь
dict_scalers ={
    'MinMaxScaler': MinMaxScaler(),
    'RobustScaler':RobustScaler(),
    'StandardScaler':StandardScaler(),
}

# с помощью функции corr_transform_to_force получим
# список не коррелируемых признаков
list_ncorr_features = corr_transform_to_force(corr_matrix,threshold=best_threshold)[1]

# обьявим scaler
scaler = dict_scalers[best_scaler]

# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
y_train_pd = pd.read_csv('target/target_train.csv')

# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)

# подготовим данные для обучения модели
# с помощью функции class_1_percent_samples зададим долю 
# класса 1
list_c1_percent_id = class_1_percent_samples(y_train_pd,best_class_1_percent,random_state=best_random_state)[:1000000]

# подготовим данные для обучения
X_train_s_balanced = scaler.fit_transform(X_train_pd.loc[list_c1_percent_id])
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

# освободим память от "тяжелых" и ненужных файлов
del X_train_pd, y_train_pd
gc.collect()


# обучаем модель LogisticRegression с наилучшеми параметрами
logistic_regression = linear_model.LogisticRegression(
        **best_param_lr,
        random_state=42,
        max_iter=10000)
logistic_regression.fit(X_train_s_balanced, y_train_balanced)

# удаляем крупные файлы чтобы высвободить память 
del X_train_s_balanced, y_train_balanced
gc.collect()

# загружаем тестовые наборы
# сформируем данные для анализа сбалансированности обучающих данных
X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()[list_ncorr_features]
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

# подготовим данные для проверки модели
X_train_s = scaler.transform(X_train)
X_valid_s = scaler.transform(X_valid)

# удаляем крупные файлы чтобы высвободить память 
del X_train, X_valid
gc.collect()

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_lr_pred_proba = logistic_regression.predict_proba(X_train_s)[:,1]
y_valid_lr_pred_proba = logistic_regression.predict_proba(X_valid_s)[:,1]

# Делаем предсказание для валидационной выборки
y_valid_lr_pred = logistic_regression.predict(X_valid_s)

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_lr_pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_lr_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_lr_pred,zero_division=0))

# time: 2m 30s

ROC AUC на обучающем наборе 0.665
ROC AUC на валидационном наборе 0.662
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.97      0.99      0.98     68747
           1       0.11      0.03      0.04      2503

    accuracy                           0.96     71250
   macro avg       0.54      0.51      0.51     71250
weighted avg       0.94      0.96      0.95     71250



#### <span style="color:MediumBlue">Построение модели Random Forest Classifier</span>

##### <span style="color:MediumSlateBlue">Формирование данных для обучения</span>

Анализ исходных данных, в частности target, показал что представленные данные   
имееют перекос: 96% клиентов у которых не случился дефолт (flag = 0),    
против 4 % - для которых произошел дефолт (flag = 1).  
С помощью функции class_1_percent_samples, сформируем сбаланисрованную выборку  
для обучения моделей.
За основу сбалансировных данных возьмем данные клиентов с дефолтом  
и к ним будем добирать необходимое количество клиентов до сбалансированности. 


Функция class_1_percent_samples принемает две переменные:
- target_data - массив с id и целевой переменной
- class_1_percent - процент класса 1 в результирующем массиве

In [1058]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'payments'
count_features = dict_spaces[feature_space]

In [1059]:
# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

In [1060]:
# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)
y_train_pd.head(4)

id  flag
id                    
1825800  1825800     0
2166483  2166483     0
2534345  2534345     0
1803283  1803283     0

In [1061]:
# взглянем на сблансиорованность данных в y_train
y_train_pd['flag'].value_counts(normalize=True)

flag
0    0.964242
1    0.035758
Name: proportion, dtype: float64

In [1062]:
# сбалансируем данные в y_train_pd
list_c1_percent_id = class_1_percent_samples(y_train_pd,0.5)
# list_c1_percent_features - список 'id' из y_train_pd соотвествующих  
# заданному проценту класса 1
len(list_c1_percent_id)

45860

In [1063]:
# проверим сбалансированность полученного y_train
y_train_pd.loc[list_c1_percent_id]['flag'].value_counts(normalize=True)

flag
1    0.5
0    0.5
Name: proportion, dtype: float64

В отличие от данных в *transform_data_torow*, где модели показываеются последние N  
операций клиента, в данные в *transform_data_stat* сфомированы из различных статистических   
характеристик ряда определяющего клиентскую историю в банке. 

Соотвественно, если в данных *transform_data_torow* была сильная корреляция между признаками,  
то я не смог бы ее убрать, иначе потярется смысл "показать последовательный ряд в историии клиента".  
Признаки в *transform_data_stat* не имеют такой особенности. Поэтому, необходимо проанализировать  
данные в *transform_data_stat* и, в случае сильной коррреляции признаков, устранить ее.

In [1064]:
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()
corr_matrix.shape

(426, 426)

In [1065]:
# с помощью функции corr_transrom_to_power получим
# силу корреляции матрицы и список не коррелируемых признаков

# для начального анализа зададим порог силы корреляции, при котором признаки 
# будут отнесены к "сильно скоррелированными" равным 0.6
ncorr_matrix,list_ncorr_features,corr_power =corr_transform_to_force(corr_matrix,threshold=0.6)

# Выведем результаты преобразования
print('Исходное количество признаков: ', corr_matrix.shape[0])
print('Количество не коррелируемых признаков: ', len(list_ncorr_features))
# сила корреляции признаков
print('Отношение коррелируемых исходному количеству признаков (сила корреляции): ',corr_power)

Исходное количество признаков:  426
Количество не коррелируемых признаков:  54
Отношение коррелируемых исходному количеству признаков (сила корреляции):  0.873


In [1066]:
# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']
# сформируем данные для проверики модели
# сформируем данные для анализа сбалансированности обучающих данных
X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()
y_train = pd.read_csv('target/target_train.csv')['flag']
X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()
y_valid = pd.read_csv('target/target_valid.csv')['flag']

In [1067]:
# посмотрим на структуру данных в X_train_balanced
X_train_balanced.head(4)

f1   f2     f3   f4   f5     f6     f7   f8     f9  f10  ...  \
id                                                                  ...   
2335465  17.0  3.0  0.294  0.0  0.0  2.835  0.294  0.0  0.749  0.0  ...   
390270    6.0  3.0  0.500  0.0  0.0  2.894  0.500  0.0  1.118  0.0  ...   
2494034  14.0  3.0  0.214  0.0  0.0  2.846  0.214  0.0  0.773  0.0  ...   
2018674  15.0  3.0  0.200  0.0  0.0  2.842  0.200  0.0  0.748  0.0  ...   

          f417  f418  f419  f420  f421  f422  f423  f424   f425  f426  
id                                                                     
2335465  1.273   1.0   1.6   4.0   4.0   4.0   4.0  0.76  1.721   2.5  
390270   0.000   4.0   4.0   4.0   4.0   4.0   4.0  1.00  0.000   4.0  
2494034  0.000   4.0   4.0   4.0   4.0   4.0   4.0  1.00  0.000   4.0  
2018674  1.200   1.0   3.4   4.0   4.0   4.0   4.0  0.80  1.543   2.5  

[4 rows x 426 columns]

In [1068]:
# посмотрим на структуру данных в y_train_balanced
y_train_balanced.head(4)

id
2335465    1
390270     1
2494034    1
2018674    1
Name: flag, dtype: int64

In [1069]:
# проверим что выборки действительно совпадают по id
X_train_balanced.index.to_list() == y_train_balanced.index.to_list()

True

##### <span style="color:MediumSlateBlue">Baseline обучение модели RandomForestClassifier</span>

In [1070]:
# обучаем модель логистической регрессии
# чтобы модель пыталась найти связь во всех признаках
random_forest = RandomForestClassifier(random_state=42, n_jobs=-1)
random_forest.fit(X_train_balanced[list_ncorr_features],y_train_balanced)

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_rf__pred_proba = random_forest.predict_proba(X_train[list_ncorr_features])[:,1]
y_valid_rf_pred_proba = random_forest.predict_proba(X_valid[list_ncorr_features])[:,1]

# Делаем предсказание для валидационной выборки
y_valid_rf_pred = random_forest.predict(X_valid[list_ncorr_features])

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_rf__pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_rf_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_rf_pred))

# time: 17s

ROC AUC на обучающем наборе 0.894
ROC AUC на валидационном наборе 0.626
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.98      0.61      0.75     68747
           1       0.05      0.58      0.09      2503

    accuracy                           0.61     71250
   macro avg       0.51      0.59      0.42     71250
weighted avg       0.94      0.61      0.73     71250



##### <span style="color:MediumSlateBlue">Подбор гиперпараметров модели</span>

In [1784]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'payments'
count_features = dict_spaces[feature_space]

# для работы функции corr_transform_to_force
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()

# настроим оптимизацию гипер параметров
def optuna_rf(trial):
  # задаем пространства поиска гиперпараметров
  # задаем пространства поиска гиперпараметров
  n_estimators = trial.suggest_int('n_estimators', 40, 100,step = 5)
  criterion = trial.suggest_categorical('criterion',['gini', 'entropy', 'log_loss'])
  max_depth = trial.suggest_int('max_depth', 10, 30,step = 1)
  min_samples_split = trial.suggest_int('min_samples_split', 5, 15,step = 1)
  min_samples_leaf = trial.suggest_int('min_samples_leaf', 5, 15,step = 1)
  max_features = trial.suggest_float('max_features',0.4,0.8)
  max_samples = trial.suggest_float('max_samples',0.4,0.8)
  class_0_weight = trial.suggest_float('class_0_weight',0.1,1)
  class_1_weight = trial.suggest_float('class_1_weight',0.1,1)
  threshold = trial.suggest_float('threshold',0.4,0.8)
  class_1_percent = trial.suggest_float('class_1_percent',0.01,0.5)
  random_state = trial.suggest_int('random_state', 1, 1000000)


  # создаем модель
  optuna_random_forest = RandomForestClassifier(
      n_estimators = n_estimators, 
      criterion = criterion,
      max_depth = max_depth,
      min_samples_split = min_samples_split,  
      min_samples_leaf = min_samples_leaf,
      max_features=max_features,
      max_samples=max_samples,
      class_weight={0:class_0_weight,1:class_1_weight},
      n_jobs=-1,
      random_state=42)

  # с помощью функции corr_transform_to_force получим
  # список не коррелируемых признаков
  list_ncorr_features = corr_transform_to_force(corr_matrix,threshold=threshold)[1]

  # сформируем данные для анализа сбалансированности обучающих данных
  X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
  y_train_pd = pd.read_csv('target/target_train.csv')

  # поготовим данные y_train_pd к работе с функцией class_1_percent_samples
  y_train_pd.set_index('id',drop=False,inplace=True)

  # подготовим данные для обучения модели
  # с помощью функции class_1_percent_samples зададим долю 
  # класса 1
  list_c1_percent_id = class_1_percent_samples(y_train_pd,class_1_percent,random_state=random_state)[:1000000]

  # подготовим данные для обучения
  X_train_balanced = X_train_pd.loc[list_c1_percent_id]
  y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']

  # освободим память от "тяжелых" и ненужных файлов
  del X_train_pd, y_train_pd
  gc.collect()

  # я не воспользовался параметром timeout метода optimize потому, что  
  # optimize отставливает поиск параметров, если время обучения 
  # превышает timeout. Мне нужно чтобы поиск параметров продолжился.
  try:
    # для модуля func_time_out упакуем обучение модели в функцию try_func
    def try_func():
            return optuna_random_forest.fit(X_train_balanced, y_train_balanced)
    # обучаем модель с ограничением по времени 10 минут (600 секунд)
    optuna_random_forest = func_timeout.func_timeout(600, try_func)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train_balanced, y_train_balanced
    gc.collect()

    # загружаем тестовые наборы
    # сформируем данные для анализа сбалансированности обучающих данных
    X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
    X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()[list_ncorr_features]
    y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
    y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()
    
    # делаем предсказание на обучающем и валидационном наборе
    #Считаем метрики для класса 1 добавляем их в список
    roc_train = metrics.roc_auc_score(y_train, optuna_random_forest.predict_proba(X_train)[:,1])
    roc_valid = metrics.roc_auc_score(y_valid, optuna_random_forest.predict_proba(X_valid)[:,1])
    f1_score = metrics.f1_score(y_valid, optuna_random_forest.predict(X_valid))
    recall_1 = metrics.recall_score(y_valid, optuna_random_forest.predict(X_valid),average=None,zero_division=0)[1]
    precision_1 = metrics.precision_score(y_valid, optuna_random_forest.predict(X_valid),average=None,zero_division=0)[1]

    # удаляем крупные файлы чтобы высвободить память 
    del X_train, X_valid, y_train, y_valid
    gc.collect()

  except func_timeout.FunctionTimedOut:
    # удаляем крупные файлы чтобы высвободить память 
    del X_train_balanced, y_train_balanced
    gc.collect()
    
    # фиксируем пустые значения метрик
    roc_train = 0
    roc_valid = 0
    f1_score = 0
    recall_1 = 0
    precision_1 = 0
    pass

  return roc_train, roc_valid, f1_score, recall_1, precision_1

In [1785]:
# cоздаем объект исследования
optuna_study_rf = optuna.create_study(study_name= 'RandomForestClassifier_'+feature_space+'_stat', 
                               directions=['maximize','maximize','maximize','maximize','maximize'], 
                               sampler=optuna.samplers.TPESampler(),
                               pruner='Hyperband',
                               storage='sqlite:///optuna_studies.db',
                               load_if_exists=True)
# на случай удаления 
# optuna.delete_study(study_name='RandomForestClassifier_'+feature_space+'_stat', storage='sqlite:///optuna_studies.db')

[I 2025-04-19 15:00:31,053] Using an existing study with name 'RandomForestClassifier_payments_stat' instead of creating a new one.


In [1073]:
# ищем лучшую комбинацию гиперпараметров n_trials раз
optuna_study_rf.optimize(optuna_rf, n_trials=300)

[I 2025-04-18 06:03:38,597] Trial 0 finished with values: [0.8724493978647712, 0.6591791393667672, 0.0007942811755361397, 0.00039952057530962844, 0.06666666666666667] and parameters: {'n_estimators': 45, 'criterion': 'log_loss', 'max_depth': 23, 'min_samples_split': 5, 'min_samples_leaf': 10, 'max_features': 0.6850191656981753, 'max_samples': 0.6350168463784105, 'class_0_weight': 0.5942704540799365, 'class_1_weight': 0.49747469778406417, 'threshold': 0.7903381726432884, 'class_1_percent': 0.1290758299612534, 'random_state': 66886}.
[I 2025-04-18 06:03:46,399] Trial 1 finished with values: [0.7893429959432581, 0.641749614777074, 0.09074898995131048, 0.699960047942469, 0.048519759616716056] and parameters: {'n_estimators': 55, 'criterion': 'entropy', 'max_depth': 24, 'min_samples_split': 7, 'min_samples_leaf': 8, 'max_features': 0.5492250143026846, 'max_samples': 0.6705381302179014, 'class_0_weight': 0.21661223626122006, 'class_1_weight': 0.9849392352869497, 'threshold': 0.57588174084605

In [1786]:
# из полученного результат соврмируем Data Frame
optuna_study_rf_pd = optuna_study_rf.trials_dataframe().dropna()
# переименуем столбы
optuna_study_rf_pd.rename(columns={
    'values_0': 'roc_train',
    'values_1': 'roc_valid',
    'values_2': 'f1_score',
    'values_3': 'recall_1',
    'values_4': 'precision_1'
},inplace=True)
optuna_study_rf_pd.tail()

number  roc_train  roc_valid  f1_score  recall_1  precision_1  \
295     295   0.845102   0.655363  0.118219  0.354375     0.070943   
296     296   0.888896   0.649868  0.118360  0.265282     0.076173   
297     297   0.801388   0.653515  0.105532  0.528965     0.058613   
298     298   0.907253   0.654887  0.000000  0.000000     0.000000   
299     299   0.804650   0.657902  0.124855  0.301638     0.078720   

                datetime_start          datetime_complete  \
295 2025-04-18 07:06:59.251550 2025-04-18 07:07:14.235486   
296 2025-04-18 07:07:14.240965 2025-04-18 07:07:28.107578   
297 2025-04-18 07:07:28.113111 2025-04-18 07:07:41.074656   
298 2025-04-18 07:07:41.080184 2025-04-18 07:08:04.676027   
299 2025-04-18 07:08:04.682095 2025-04-18 07:08:18.612337   

                  duration  params_class_0_weight  ...  params_criterion  \
295 0 days 00:00:14.983936               0.342153  ...          log_loss   
296 0 days 00:00:13.866613               0.317531  ...          log_loss   
297 0 days 00:00:12.961545               0.263612  ...          log_loss   
298 0 days 00:00:23.595843               0.762390  ...           entropy   
299 0 days 00:00:13.930242               0.456752  ...          log_loss   

     params_max_depth params_max_features  params_max_samples  \
295                29            0.474103            0.766758   
296                30            0.431568            0.784418   
297                29            0.499176            0.474078   
298                28            0.450475            0.776420   
299                30            0.481062            0.611347   

     params_min_samples_leaf  params_min_samples_split  params_n_estimators  \
295                       12                        12                   70   
296                        6                        11                   75   
297                        9                        10                   80   
298                       11                         9                   75   
299                       15                        14                   60   

     params_random_state  params_threshold     state  
295               186075          0.773028  COMPLETE  
296               999017          0.694832  COMPLETE  
297               108327          0.718515  COMPLETE  
298               918263          0.794051  COMPLETE  
299               954762          0.779078  COMPLETE  

[5 rows x 22 columns]

In [1787]:
# покаждем статистику обучения
print('Максимальное значение метрики ROC AUC на валидационном наборе:',round(optuna_study_rf_pd['roc_valid'].max(),3))
print('Среднее значение метрики ROC AUC на валидационном наборе:',round(optuna_study_rf_pd['roc_valid'].mean(),3))
print('Максимальное значение метрики f1_score на валидационном наборе:',round(optuna_study_rf_pd['f1_score'].max(),3))
print('Среднее значение метрики f1_score на валидационном наборе:',round(optuna_study_rf_pd['f1_score'].mean(),3))
print('Максимальное значение метрики recall_1 на валидационном наборе:',round(optuna_study_rf_pd['recall_1'].max(),3))
print('Среднее значение метрики recall_1 на валидационном наборе:',round(optuna_study_rf_pd['recall_1'].mean(),3))
print('Максимальное значение метрики precision_1 на валидационном наборе:',round(optuna_study_rf_pd['precision_1'].max(),3))
print('Среднее значение метрики precision_1 на валидационном наборе:',round(optuna_study_rf_pd['precision_1'].mean(),3))

Максимальное значение метрики ROC AUC на валидационном наборе: 0.669
Среднее значение метрики ROC AUC на валидационном наборе: 0.654
Максимальное значение метрики f1_score на валидационном наборе: 0.131
Среднее значение метрики f1_score на валидационном наборе: 0.095
Максимальное значение метрики recall_1 на валидационном наборе: 0.984
Среднее значение метрики recall_1 на валидационном наборе: 0.339
Максимальное значение метрики precision_1 на валидационном наборе: 1.0
Среднее значение метрики precision_1 на валидационном наборе: 0.08


In [1790]:
# Построим зависимость метрик качества модели от number

fig = px.scatter(
    data_frame=optuna_study_rf_pd[(optuna_study_rf_pd['roc_valid']>=0.999*optuna_study_rf_pd['roc_valid'].max())],
    x='number', #ось абсцисс
    y=['roc_valid','roc_train','precision_1','recall_1','f1_score'], #ось ординат
)
fig.update_layout(
    title ={
        'text':'Зависимость качества модели от trials optuna', # Имя рабочей плоскости
        'font':{'size':35,'family':"Times New Roman"}, # размер и стиль написания имени рабочей плоскости
        'x':0.5, # Смешение имени по оси "x" на половину рабочей плоскости
        },
    height =800,# Высота рабочей плоскости
    width = 1350, # Ширина рабочей плоскости
    bargap=0.2, # Добавил расстояния между столбами гистограммы
    xaxis_title='trials optuna',
    yaxis_title='Величина параметра')
fig.update_xaxes(showspikes=True)
fig.update_yaxes(showspikes=True)

fig.show()

<span style="color:Blue">

Вывод:  

Их всех выбираем точку $number =281$.   
Не смотря на, то что в этой точке модель подает признаки переобучеености,  
в этой точке оптимальные значения метрик $recall_1$ и $precision_1$, а  
также относительно высокая метрика $ROC AUC$.   
Посмотрим каким значениям гиперпараметров соотвествует выбраннаяточка.

In [1791]:
# определим номер лучшге варианта
best_optuna_number = 281

# сформируем словарь лучших гипирпарметров RandomForestClassifier
best_param_rf = {
    'n_estimators' : int(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_n_estimators'].iloc[0]),
    'criterion': optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_criterion'].iloc[0],
    'max_depth' : int(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_max_depth'].iloc[0]),
    'min_samples_split': int(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_min_samples_split'].iloc[0]),
    'min_samples_leaf' : int(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_min_samples_leaf'].iloc[0]),
    'max_features': optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_max_features'].iloc[0],
    'max_samples' : optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_max_samples'].iloc[0],
    'class_weight' : {0:optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_class_0_weight'].iloc[0],
                      1:optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_class_1_weight'].iloc[0]}
    }

# определим перменные для лучших значений параметров
best_threshold = optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_threshold'].iloc[0]
best_class_1_percent = optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_class_1_percent'].iloc[0]
best_random_state = optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_random_state'].iloc[0]


# Выведем принятые наилучшие праметры
print('best n estimators:',best_param_rf['n_estimators'])
print('best criterion:',best_param_rf['criterion'])
print('best max depth:',best_param_rf['max_depth'])
print('best min samples split:',best_param_rf['min_samples_split'])
print('best min samples leaf:',best_param_rf['min_samples_leaf'])
print('best max features(%):',round(best_param_rf['max_features'],3))
print('best max samples(%):',round(best_param_rf['max_samples'],3))
print('best class 0 weight:',round(best_param_rf['class_weight'][0],3))
print('best class 1 weight:',round(best_param_rf['class_weight'][1],3))

print('best class 1 percent:',round(best_class_1_percent,3))
print('best threshold:',round(best_threshold,3))
print('best random state:', best_random_state)
print('time for best train:',round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['duration'].iloc[0].seconds/60),'minutes')

print()
print('ROC AUC на обучающем наборе:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['roc_train'].iloc[0],3))
print('ROC AUC на валидационном наборе:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['roc_valid'].iloc[0],3))
print('precision класса 1:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['precision_1'].iloc[0],3))
print('recall класса 1:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['recall_1'].iloc[0],3))

best n estimators: 75
best criterion: log_loss
best max depth: 11
best min samples split: 11
best min samples leaf: 15
best max features(%): 0.481
best max samples(%): 0.761
best class 0 weight: 0.322
best class 1 weight: 0.258
best class 1 percent: 0.14
best threshold: 0.785
best random state: 959721
time for best train: 0 minutes

ROC AUC на обучающем наборе: 0.727
ROC AUC на валидационном наборе: 0.669
precision класса 1: 1.0
recall класса 1: 0.0


##### <span style="color:MediumSlateBlue">Обучение модели с лучшими параметрами</span>

In [1792]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'payments'
count_features = dict_spaces[feature_space]

# для работы функции corr_transform_to_force
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()

# с помощью функции corr_transform_to_force получим
# список не коррелируемых признаков
list_ncorr_features = corr_transform_to_force(corr_matrix,threshold=best_threshold)[1]

# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
y_train_pd = pd.read_csv('target/target_train.csv')

# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)

# подготовим данные для обучения модели
# с помощью функции class_1_percent_samples зададим долю 
# класса 1
list_c1_percent_id = class_1_percent_samples(y_train_pd,best_class_1_percent,random_state=best_random_state)[:1000000]

# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']

# освободим память от "тяжелых" и ненужных файлов
del X_train_pd, y_train_pd
gc.collect()


# обучаем модель RandomForestClassifier с наилучшеми параметрами
random_forest = RandomForestClassifier(
        **best_param_rf,
        n_jobs=-1,
        random_state=42)
random_forest.fit(X_train_balanced, y_train_balanced)

# удаляем крупные файлы чтобы высвободить память 
del X_train_balanced, y_train_balanced
gc.collect()

# загружаем тестовые наборы
# сформируем данные для анализа сбалансированности обучающих данных
X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()[list_ncorr_features]
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_rf_pred_proba = random_forest.predict_proba(X_train)[:,1]
y_valid_rf_pred_proba = random_forest.predict_proba(X_valid)[:,1]

# Делаем предсказание для валидационной выборки
y_valid_rf_pred = random_forest.predict(X_valid)

# удаляем крупные файлы чтобы высвободить память 
del X_train, X_valid
gc.collect()

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_rf_pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_rf_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_rf_pred,zero_division=0))

# time: 5m 30s

ROC AUC на обучающем наборе 0.727
ROC AUC на валидационном наборе 0.669
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.96      1.00      0.98     68747
           1       1.00      0.00      0.00      2503

    accuracy                           0.96     71250
   macro avg       0.98      0.50      0.49     71250
weighted avg       0.97      0.96      0.95     71250



#### <span style="color:MediumBlue">Построение модели Gradient Boosting Classifier</span>

##### <span style="color:MediumSlateBlue">Формирование данных для обучения</span>

Анализ исходных данных, в частности target, показал что представленные данные   
имееют перекос: 96% клиентов у которых не случился дефолт (flag = 0),    
против 4 % - для которых произошел дефолт (flag = 1).  
С помощью функции class_1_percent_samples, сформируем сбаланисрованную выборку  
для обучения моделей.
За основу сбалансировных данных возьмем данные клиентов с дефолтом  
и к ним будем добирать необходимое количество клиентов до сбалансированности. 


Функция class_1_percent_samples принемает две переменные:
- target_data - массив с id и целевой переменной
- class_1_percent - процент класса 1 в результирующем массиве

In [1090]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'payments'
count_features = dict_spaces[feature_space]

In [1091]:
# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

In [1092]:
# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)
y_train_pd.head(4)

id  flag
id                    
1825800  1825800     0
2166483  2166483     0
2534345  2534345     0
1803283  1803283     0

In [1093]:
# взглянем на сблансиорованность данных в y_train
y_train_pd['flag'].value_counts(normalize=True)

flag
0    0.964242
1    0.035758
Name: proportion, dtype: float64

In [1094]:
# сбалансируем данные в y_train_pd
list_c1_percent_id = class_1_percent_samples(y_train_pd,0.5)
# list_c1_percent_features - список 'id' из y_train_pd соотвествующих  
# заданному проценту класса 1
len(list_c1_percent_id)

45860

In [1095]:
# проверим сбалансированность полученного y_train
y_train_pd.loc[list_c1_percent_id]['flag'].value_counts(normalize=True)

flag
1    0.5
0    0.5
Name: proportion, dtype: float64

В отличие от данных в *transform_data_torow*, где модели показываеются последние N  
операций клиента, в данные в *transform_data_stat* сфомированы из различных статистических   
характеристик ряда определяющего клиентскую историю в банке. 

Соотвественно, если в данных *transform_data_torow* была сильная корреляция между признаками,  
то я не смог бы ее убрать, иначе потярется смысл "показать последовательный ряд в историии клиента".  
Признаки в *transform_data_stat* не имеют такой особенности. Поэтому, необходимо проанализировать  
данные в *transform_data_stat* и, в случае сильной коррреляции признаков, устранить ее.

In [1096]:
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()
corr_matrix.shape

(426, 426)

In [1097]:
# с помощью функции corr_transrom_to_power получим
# силу корреляции матрицы и список не коррелируемых признаков

# для начального анализа зададим порог силы корреляции, при котором признаки 
# будут отнесены к "сильно скоррелированными" равным 0.6
ncorr_matrix,list_ncorr_features,corr_power =corr_transform_to_force(corr_matrix,threshold=0.6)

# Выведем результаты преобразования
print('Исходное количество признаков: ', corr_matrix.shape[0])
print('Количество не коррелируемых признаков: ', len(list_ncorr_features))
# сила корреляции признаков
print('Отношение коррелируемых исходному количеству признаков (сила корреляции): ',corr_power)

Исходное количество признаков:  426
Количество не коррелируемых признаков:  54
Отношение коррелируемых исходному количеству признаков (сила корреляции):  0.873


In [1098]:
# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']
# сформируем данные для проверики модели
# сформируем данные для анализа сбалансированности обучающих данных
X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()
y_train = pd.read_csv('target/target_train.csv')['flag']
X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()
y_valid = pd.read_csv('target/target_valid.csv')['flag']

In [1099]:
# посмотрим на структуру данных в X_train_balanced
X_train_balanced.head(4)

f1   f2     f3   f4   f5     f6     f7   f8     f9  f10  ...  \
id                                                                  ...   
2335465  17.0  3.0  0.294  0.0  0.0  2.835  0.294  0.0  0.749  0.0  ...   
390270    6.0  3.0  0.500  0.0  0.0  2.894  0.500  0.0  1.118  0.0  ...   
2494034  14.0  3.0  0.214  0.0  0.0  2.846  0.214  0.0  0.773  0.0  ...   
2018674  15.0  3.0  0.200  0.0  0.0  2.842  0.200  0.0  0.748  0.0  ...   

          f417  f418  f419  f420  f421  f422  f423  f424   f425  f426  
id                                                                     
2335465  1.273   1.0   1.6   4.0   4.0   4.0   4.0  0.76  1.721   2.5  
390270   0.000   4.0   4.0   4.0   4.0   4.0   4.0  1.00  0.000   4.0  
2494034  0.000   4.0   4.0   4.0   4.0   4.0   4.0  1.00  0.000   4.0  
2018674  1.200   1.0   3.4   4.0   4.0   4.0   4.0  0.80  1.543   2.5  

[4 rows x 426 columns]

In [1100]:
# посмотрим на структуру данных в y_train_balanced
y_train_balanced.head(4)

id
2335465    1
390270     1
2494034    1
2018674    1
Name: flag, dtype: int64

In [1101]:
# проверим что выборки действительно совпадают по id
X_train_balanced.index.to_list() == y_train_balanced.index.to_list()

True

##### <span style="color:MediumSlateBlue">Baseline обучение модели Hist Gradient Boosting Classifier</span>

In [1102]:
# обучаем модель Gradient Boosting Classifier
gradient_boosting = HistGradientBoostingClassifier(random_state=42)
gradient_boosting.fit(X_train_balanced[list_ncorr_features],y_train_balanced)

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_rf__pred_proba = gradient_boosting.predict_proba(X_train[list_ncorr_features])[:,1]
y_valid_rf_pred_proba = gradient_boosting.predict_proba(X_valid[list_ncorr_features])[:,1]

# Делаем предсказание для валидационной выборки
y_valid_rf_pred = gradient_boosting.predict(X_valid[list_ncorr_features])

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_rf__pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_rf_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_rf_pred))

# time: 30s

ROC AUC на обучающем наборе 0.674
ROC AUC на валидационном наборе 0.659
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.98      0.65      0.78     68747
           1       0.06      0.58      0.10      2503

    accuracy                           0.64     71250
   macro avg       0.52      0.61      0.44     71250
weighted avg       0.94      0.64      0.75     71250



##### <span style="color:MediumSlateBlue">Подбор гиперпараметров модели</span>

In [1793]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'payments'
count_features = dict_spaces[feature_space]

# для работы функции corr_transform_to_force
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()

# настроим оптимизацию гипер параметров
def optuna_hgbc(trial):
  # задаем пространства поиска гиперпараметров
  learning_rate = trial.suggest_float('learning_rate',0.01,0.1)
  max_iter = trial.suggest_int('max_iter', 150, 250,step = 1)
  max_leaf_nodes = trial.suggest_int('max_leaf_nodes', 2, 60,step = 1)
  max_depth = trial.suggest_int('max_depth', 1, 10,step = 1)
  min_samples_leaf = trial.suggest_int('min_samples_leaf', 1, 60,step = 1)
  max_features = trial.suggest_float('max_features',0.6,1)
  l2_regularization = trial.suggest_float('l2_regularization',0.01,1)
  class_0_weight = trial.suggest_float('class_0_weight',0.01,1)
  class_1_weight = trial.suggest_float('class_1_weight',0.5,1)
  threshold = trial.suggest_float('threshold',0.7,1)
  class_1_percent = trial.suggest_float('class_1_percent',0.01,0.25)
  random_state = trial.suggest_int('random_state', 1, 1000000)

  # создаем модель
  optuna_gradient_boosting = HistGradientBoostingClassifier(
      learning_rate= learning_rate,
      max_iter = max_iter,
      max_leaf_nodes =max_leaf_nodes,
      max_depth = max_depth,
      min_samples_leaf = min_samples_leaf,
      max_features=max_features,
      l2_regularization = l2_regularization,
      class_weight={0:class_0_weight,1:class_1_weight},
      random_state=42)

  # с помощью функции corr_transform_to_force получим
  # список не коррелируемых признаков
  list_ncorr_features = corr_transform_to_force(corr_matrix,threshold=threshold)[1]

  # сформируем данные для анализа сбалансированности обучающих данных
  X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
  y_train_pd = pd.read_csv('target/target_train.csv')

  # поготовим данные y_train_pd к работе с функцией class_1_percent_samples
  y_train_pd.set_index('id',drop=False,inplace=True)

  # подготовим данные для обучения модели
  # с помощью функции class_1_percent_samples зададим долю 
  # класса 1
  list_c1_percent_id = class_1_percent_samples(y_train_pd,class_1_percent,random_state=random_state)[:1000000]

  # подготовим данные для обучения
  X_train_balanced = X_train_pd.loc[list_c1_percent_id]
  y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']

  # освободим память от "тяжелых" и ненужных файлов
  del X_train_pd, y_train_pd
  gc.collect()

  # я не воспользовался параметром timeout метода optimize потому, что  
  # optimize отставливает поиск параметров, если время обучения 
  # превышает timeout. Мне нужно чтобы поиск параметров продолжился.
  try:
    # для модуля func_time_out упакуем обучение модели в функцию try_func
    def try_func():
            return optuna_gradient_boosting.fit(X_train_balanced,y_train_balanced)
    # обучаем модель с ограничением по времени 10 минут (600 секунд)
    optuna_gradient_boosting = func_timeout.func_timeout(600, try_func)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train_balanced, y_train_balanced
    gc.collect()

        # загружаем тестовые наборы
    # сформируем данные для анализа сбалансированности обучающих данных
    X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
    X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()[list_ncorr_features]
    y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
    y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()
    
    # делаем предсказание на обучающем и валидационном наборе и считаем метрики
    roc_train = metrics.roc_auc_score(y_train, optuna_gradient_boosting.predict_proba(X_train)[:,1])
    roc_valid = metrics.roc_auc_score(y_valid, optuna_gradient_boosting.predict_proba(X_valid)[:,1])
    f1_score = metrics.f1_score(y_valid, optuna_gradient_boosting.predict(X_valid))
    recall_1 = metrics.recall_score(y_valid, optuna_gradient_boosting.predict(X_valid),average=None,zero_division=0)[1]
    precision_1 = metrics.precision_score(y_valid, optuna_gradient_boosting.predict(X_valid),average=None,zero_division=0)[1]


    # удаляем крупные файлы чтобы высвободить память 
    del X_train, X_valid, y_train, y_valid
    gc.collect()

  except func_timeout.FunctionTimedOut:
    # удаляем крупные файлы чтобы высвободить память 
    del X_train_balanced, y_train_balanced
    gc.collect()
    
    # фиксируем пустые значения метрик
    roc_train = 0
    roc_valid = 0
    f1_score = 0
    recall_1 = 0
    precision_1 = 0
    pass

  return roc_train, roc_valid, f1_score, recall_1, precision_1

In [1794]:
# cоздаем объект исследования
# чтобы модель не переобучалась минимизируем roc_train 
# и максимизируем roc_valid
optuna_study_hgbc = optuna.create_study(study_name='HistGradientBoostingClassifier_'+feature_space+'_stat', 
                               directions=['maximize','maximize','maximize','maximize','maximize'], 
                               sampler=optuna.samplers.TPESampler(),
                               pruner='Hyperband',
                               storage='sqlite:///optuna_studies.db',
                               load_if_exists=True)

# ну случай удаления обучения
# optuna.delete_study(study_name='HistGradientBoostingClassifier'+feature_space+'_stat', storage='sqlite:///optuna_studies.db')

[I 2025-04-19 15:02:04,727] Using an existing study with name 'HistGradientBoostingClassifier_payments_stat' instead of creating a new one.


In [1105]:
# ищем лучшую комбинацию гиперпараметров n_trials раз
optuna_study_hgbc.optimize(optuna_hgbc, n_trials=300)

[I 2025-04-18 07:08:58,476] Trial 0 finished with values: [0.679489144282861, 0.6689314321352495, 0.10981954153796131, 0.539752297243308, 0.06112845572598525] and parameters: {'learning_rate': 0.0982572091973395, 'max_iter': 243, 'max_leaf_nodes': 23, 'max_depth': 3, 'min_samples_leaf': 56, 'max_features': 0.8407798076495667, 'l2_regularization': 0.32650764895135587, 'class_0_weight': 0.1871992768669416, 'class_1_weight': 0.8585980239989137, 'threshold': 0.9822177393509731, 'class_1_percent': 0.16986061752417356, 'random_state': 994436}.
[I 2025-04-18 07:09:19,068] Trial 1 finished with values: [0.6748945080537576, 0.6670459236427017, 0.0, 0.0, 0.0] and parameters: {'learning_rate': 0.08068387349730244, 'max_iter': 212, 'max_leaf_nodes': 5, 'max_depth': 3, 'min_samples_leaf': 15, 'max_features': 0.7192142523831145, 'l2_regularization': 0.4930553586502993, 'class_0_weight': 0.7582883649913138, 'class_1_weight': 0.6278554719011984, 'threshold': 0.9200480096432255, 'class_1_percent': 0.04

In [1795]:
# из полученного результат соврмируем Data Frame
optuna_study_hgbc_pd = optuna_study_hgbc.trials_dataframe()
# переименуем столбы
optuna_study_hgbc_pd.rename(columns={
    'values_0': 'roc_train',
    'values_1': 'roc_valid',
    'values_2': 'f1_score',
    'values_3': 'recall_1',
    'values_4': 'precision_1'
},inplace=True)
optuna_study_hgbc_pd.tail(5)

number  roc_train  roc_valid  f1_score  recall_1  precision_1  \
295     295   0.708962   0.669686  0.000000  0.000000     0.000000   
296     296   0.710331   0.669570  0.111507  0.518977     0.062464   
297     297   0.678638   0.668736  0.067854  0.999600     0.035119   
298     298   0.717063   0.668189  0.111311  0.123851     0.101076   
299     299   0.715777   0.667357  0.024079  0.013184     0.138655   

                datetime_start          datetime_complete  \
295 2025-04-18 08:21:15.356892 2025-04-18 08:21:40.087677   
296 2025-04-18 08:21:40.093718 2025-04-18 08:21:58.594446   
297 2025-04-18 08:21:58.600029 2025-04-18 08:22:13.917352   
298 2025-04-18 08:22:13.922343 2025-04-18 08:22:32.272266   
299 2025-04-18 08:22:32.277318 2025-04-18 08:22:49.856926   

                  duration  params_class_0_weight  ...  \
295 0 days 00:00:24.730785               0.784899  ...   
296 0 days 00:00:18.500728               0.228401  ...   
297 0 days 00:00:15.317323               0.012312  ...   
298 0 days 00:00:18.349923               0.467944  ...   
299 0 days 00:00:17.579608               0.476834  ...   

     params_l2_regularization  params_learning_rate  params_max_depth  \
295                  0.779860              0.055058                 7   
296                  0.757643              0.060226                 9   
297                  0.367588              0.088766                 3   
298                  0.697785              0.097828                 9   
299                  0.717321              0.098596                10   

     params_max_features  params_max_iter  params_max_leaf_nodes  \
295             0.633243              153                     58   
296             0.657559              236                     57   
297             0.940840              158                     42   
298             0.649819              201                     59   
299             0.620942              196                     60   

     params_min_samples_leaf  params_random_state  params_threshold     state  
295                       32                  162          0.949019  COMPLETE  
296                       20                57248          0.958114  COMPLETE  
297                       40               694482          0.849162  COMPLETE  
298                       35                33302          0.980838  COMPLETE  
299                       33               186630          0.985073  COMPLETE  

[5 rows x 22 columns]

In [1796]:
# покаждем статистику обучения
print('Максимальное значение метрики ROC AUC на валидационном наборе:',round(optuna_study_hgbc_pd['roc_valid'].max(),3))
print('Среднее значение метрики ROC AUC на валидационном наборе:',round(optuna_study_hgbc_pd['roc_valid'].mean(),3))
print('Максимальное значение метрики f1_score на валидационном наборе:',round(optuna_study_hgbc_pd['f1_score'].max(),3))
print('Среднее значение метрики f1_score на валидационном наборе:',round(optuna_study_hgbc_pd['f1_score'].mean(),3))
print('Максимальное значение метрики recall_1 на валидационном наборе:',round(optuna_study_hgbc_pd['recall_1'].max(),3))
print('Среднее значение метрики recall_1 на валидационном наборе:',round(optuna_study_hgbc_pd['recall_1'].mean(),3))
print('Максимальное значение метрики precision_1 на валидационном наборе:',round(optuna_study_hgbc_pd['precision_1'].max(),3))
print('Среднее значение метрики precision_1 на валидационном наборе:',round(optuna_study_hgbc_pd['precision_1'].mean(),3))

Максимальное значение метрики ROC AUC на валидационном наборе: 0.672
Среднее значение метрики ROC AUC на валидационном наборе: 0.668
Максимальное значение метрики f1_score на валидационном наборе: 0.134
Среднее значение метрики f1_score на валидационном наборе: 0.09
Максимальное значение метрики recall_1 на валидационном наборе: 1.0
Среднее значение метрики recall_1 на валидационном наборе: 0.337
Максимальное значение метрики precision_1 на валидационном наборе: 1.0
Среднее значение метрики precision_1 на валидационном наборе: 0.089


In [1799]:
# Построим зависимость метрик качества модели от number

fig = px.scatter(
    data_frame=optuna_study_hgbc_pd[(optuna_study_hgbc_pd['roc_valid']>0.9999*optuna_study_hgbc_pd['roc_valid'].max())],
    x='number', #ось абсцисс
    y=['roc_train','roc_valid','recall_1','precision_1'], #ось ординат
)
fig.update_layout(
    title ={
        'text':'Зависимость качества модели от trials optuna', # Имя рабочей плоскости
        'font':{'size':35,'family':"Times New Roman"}, # размер и стиль написания имени рабочей плоскости
        'x':0.5, # Смешение имени по оси "x" на половину рабочей плоскости
        },
    height =800,# Высота рабочей плоскости
    width = 1350, # Ширина рабочей плоскости
    bargap=0.2, # Добавил расстояния между столбами гистограммы
    xaxis_title='trials optuna',
    yaxis_title='Величина параметра')
fig.update_xaxes(showspikes=True)
fig.update_yaxes(showspikes=True)

fig.show()

<span style="color:Blue">

Вывод:  

Их всех выбираем точку $number =188$.   
В этой точке оптимальные значения метрик $recall_1$ и $precision_1$, а  
также относительно высокая метрика $ROC AUC$.   
Посмотрим каким значениям гиперпараметров соотвествует выбранная точка.

In [1800]:
# определим номер лучшге варианта
best_optuna_number = 188

# сформируем словарь лучших гипирпарметров HistGradientBoostingClassifier
best_param_hgbc = {
    'learning_rate' : optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_learning_rate'].iloc[0],
    'max_iter' : optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_max_iter'].iloc[0],
    'max_leaf_nodes' : optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_max_leaf_nodes'].iloc[0],
    'max_depth' : optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_max_depth'].iloc[0],
    'min_samples_leaf' : optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_min_samples_leaf'].iloc[0],
    'max_features' : optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_max_features'].iloc[0],
    'l2_regularization' : optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_l2_regularization'].iloc[0],
    'class_weight' : {0: optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_class_0_weight'].iloc[0],
                      1: optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_class_1_weight'].iloc[0],}
    }

# определим перменные для лучших значений параметров
best_threshold = optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_threshold'].iloc[0]
best_class_1_percent = optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_class_1_percent'].iloc[0]
best_random_state = optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_random_state'].iloc[0]


# Выведем принятые наилучшие параметры
print('best learning rate:',round(best_param_hgbc['learning_rate'],3))
print('best max iter:',best_param_hgbc['max_iter'])
print('best max leaf nodes:',best_param_hgbc['max_leaf_nodes'])
print('best max depth:',best_param_hgbc['max_depth'])
print('best min samples leaf:',best_param_hgbc['min_samples_leaf'])
print('best max features:',round(best_param_hgbc['max_features'],3))
print('best l2 regularization:',round(best_param_hgbc['l2_regularization'],3))
print('best class 0 weight:',round(best_param_hgbc['class_weight'][0],3))
print('best class 1 weight:',round(best_param_hgbc['class_weight'][1],3))

print('best class 1 percent:',round(best_class_1_percent,3))
print('best threshold:',round(best_threshold,3))
print('time for best train:',round(optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['duration'].iloc[0].seconds/60),'minutes')

print()
print('ROC AUC на обучающем наборе:', round(optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['roc_train'].iloc[0],3))
print('ROC AUC на валидационном наборе:', round(optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['roc_valid'].iloc[0],3))
print('precision класса 1:', round(optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['precision_1'].iloc[0],3))
print('recall класса 1:', round(optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['recall_1'].iloc[0],3))

best learning rate: 0.057
best max iter: 166
best max leaf nodes: 31
best max depth: 8
best min samples leaf: 28
best max features: 0.601
best l2 regularization: 0.406
best class 0 weight: 0.775
best class 1 weight: 0.804
best class 1 percent: 0.167
best threshold: 0.961
time for best train: 0 minutes

ROC AUC на обучающем наборе: 0.701
ROC AUC на валидационном наборе: 0.672
precision класса 1: 0.113
recall класса 1: 0.006


##### <span style="color:MediumSlateBlue">Обучение модели с лучшими параметрами</span>

In [1801]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'payments'
count_features = dict_spaces[feature_space]

# для работы функции corr_transform_to_force
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()

# с помощью функции corr_transform_to_force получим
# список не коррелируемых признаков
list_ncorr_features = corr_transform_to_force(corr_matrix,threshold=best_threshold)[1]

# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
y_train_pd = pd.read_csv('target/target_train.csv')

# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)

# подготовим данные для обучения модели
# с помощью функции class_1_percent_samples зададим долю 
# класса 1
list_c1_percent_id = class_1_percent_samples(y_train_pd,best_class_1_percent,random_state=best_random_state)[:1000000]

# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']

# освободим память от "тяжелых" и ненужных файлов
del X_train_pd, y_train_pd
gc.collect()

# обучаем модель HistGradientBoostingClassifier с наилучшеми параметрами
gradient_boosting = HistGradientBoostingClassifier(
        **best_param_hgbc,
        random_state=42)
gradient_boosting.fit(X_train_balanced,y_train_balanced)

# удаляем крупные файлы чтобы высвободить память 
del X_train_balanced, y_train_balanced
gc.collect()

# сформируем данные для анализа сбалансированности обучающих данных
X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()[list_ncorr_features]
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

# делаем предсказание на обучающем и валидационном наборе и считаем метрики
y_train_gb_pred_proba = gradient_boosting.predict_proba(X_train)[:,1]
y_valid_gb_pred_proba = gradient_boosting.predict_proba(X_valid)[:,1]
y_valid_gb_pred = gradient_boosting.predict(X_valid)

# удаляем крупные файлы чтобы высвободить память 
del X_train, X_valid
gc.collect()

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_gb_pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_gb_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_gb_pred,zero_division=0))

# time: 1m 40s

ROC AUC на обучающем наборе 0.701
ROC AUC на валидационном наборе 0.672
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.97      1.00      0.98     68747
           1       0.11      0.01      0.01      2503

    accuracy                           0.96     71250
   macro avg       0.54      0.50      0.50     71250
weighted avg       0.94      0.96      0.95     71250



### <span style="color:RoyalBlue">Построение модели на сбалансированных данных подпрострнства service stat</span>

#### <span style="color:MediumBlue">Построение модели Logistic Regression</span>

##### <span style="color:MediumSlateBlue">Формирование данных для обучения</span>

Анализ исходных данных, в частности target, показал что представленные данные   
имееют перекос: 96% клиентов у которых не случился дефолт (flag = 0),    
против 4 % - для которых произошел дефолт (flag = 1).  
С помощью функции class_1_percent_samples, сформируем сбаланисрованную выборку  
для обучения моделей.
За основу сбалансировных данных возьмем данные клиентов с дефолтом  
и к ним будем добирать необходимое количество клиентов до сбалансированности. 


Функция class_1_percent_samples принемает две переменные:
- target_data - массив с id и целевой переменной
- class_1_percent - процент класса 1 в результирующем массиве

In [1124]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'service'
count_features = dict_spaces[feature_space]

In [1125]:
# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

In [1126]:
# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)
y_train_pd.head(4)

id  flag
id                    
1825800  1825800     0
2166483  2166483     0
2534345  2534345     0
1803283  1803283     0

In [1127]:
# взглянем на сблансиорованность данных в y_train
y_train_pd['flag'].value_counts(normalize=True)

flag
0    0.964242
1    0.035758
Name: proportion, dtype: float64

In [1128]:
# сбалансируем данные в y_train_pd
list_c1_percent_id = class_1_percent_samples(y_train_pd,0.5)
# list_c1_percent_features - список 'id' из y_train_pd соотвествующих  
# заданному проценту класса 1
len(list_c1_percent_id)

45860

In [1129]:
# проверим сбалансированность полученного y_train
y_train_pd.loc[list_c1_percent_id]['flag'].value_counts(normalize=True)

flag
1    0.5
0    0.5
Name: proportion, dtype: float64

В отличие от данных в *transform_data_torow*, где модели показываеются последние N  
операций клиента, в данные в *transform_data_stat* сфомированы из различных статистических   
характеристик ряда определяющего клиентскую историю в банке. 

Соотвественно, если в данных *transform_data_torow* была сильная корреляция между признаками,  
то я не смог бы ее убрать, иначе потярется смысл "показать последовательный ряд в историии клиента".  
Признаки в *transform_data_stat* не имеют такой особенности. Поэтому, необходимо проанализировать  
данные в *transform_data_stat* и, в случае сильной коррреляции признаков, устранить ее.

In [1130]:
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()
corr_matrix.shape

(69, 69)

In [1131]:
# с помощью функции corr_transrom_to_power получим
# силу корреляции матрицы и список не коррелируемых признаков

# для начального анализа зададим порог силы корреляции, при котором признаки 
# будут отнесены к "сильно скоррелированными" равным 0.6
ncorr_matrix,list_ncorr_features,corr_power =corr_transform_to_force(corr_matrix,threshold=0.6)

# Выведем результаты преобразования
print('Исходное количество признаков: ', corr_matrix.shape[0])
print('Количество не коррелируемых признаков: ', len(list_ncorr_features))
# сила корреляции признаков
print('Отношение коррелируемых исходному количеству признаков (сила корреляции): ',corr_power)

Исходное количество признаков:  69
Количество не коррелируемых признаков:  26
Отношение коррелируемых исходному количеству признаков (сила корреляции):  0.623


In [1132]:
# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']
# сформируем данные для проверики модели
# сформируем данные для анализа сбалансированности обучающих данных
X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()
y_train = pd.read_csv('target/target_train.csv')['flag']
X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()
y_valid = pd.read_csv('target/target_valid.csv')['flag']

In [1133]:
# посмотрим на структуру данных в X_train_balanced
X_train_balanced.head(4)

f1   f2   f3   f4   f5   f6   f7   f8   f9  f10  ...  f60  f61  \
id                                                          ...             
2335465  17.0  0.0  1.0  1.0  1.0  1.0  1.0  0.0  0.0  1.0  ...  0.0  1.0   
390270    6.0  0.0  1.0  1.0  1.0  1.0  1.0  0.0  0.0  1.0  ...  0.0  1.0   
2494034  14.0  0.0  1.0  1.0  1.0  1.0  1.0  0.0  0.0  1.0  ...  0.0  1.0   
2018674  15.0  0.0  1.0  1.0  1.0  1.0  1.0  0.0  0.0  1.0  ...  0.0  1.0   

         f62  f63  f64  f65  f66  f67  f68  f69  
id                                               
2335465  1.0  1.0  1.0  1.0  1.0  1.0  0.0  1.0  
390270   1.0  1.0  1.0  1.0  1.0  1.0  0.0  1.0  
2494034  1.0  1.0  1.0  1.0  1.0  1.0  0.0  1.0  
2018674  1.0  1.0  1.0  1.0  1.0  1.0  0.0  1.0  

[4 rows x 69 columns]

In [1134]:
# посмотрим на структуру данных в y_train_balanced
y_train_balanced.head(4)

id
2335465    1
390270     1
2494034    1
2018674    1
Name: flag, dtype: int64

In [1135]:
# проверим что выборки действительно совпадают по id
X_train_balanced.index.to_list() == y_train_balanced.index.to_list()

True

##### <span style="color:MediumSlateBlue">Baseline обучение модели LogisticRegression</span>

In [1136]:
# обучаем модель логистической регрессии
logistic_regression = linear_model.LogisticRegression(random_state=42, max_iter=10000)
logistic_regression.fit(X_train_balanced[list_ncorr_features],y_train_balanced)

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_LR_pred_proba = logistic_regression.predict_proba(X_train[list_ncorr_features])[:,1]
y_valid_LR_pred_proba = logistic_regression.predict_proba(X_valid[list_ncorr_features])[:,1]

# Делаем предсказание для валидационной выборки
y_valid_LR_pred = logistic_regression.predict(X_valid[list_ncorr_features])

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_LR_pred_proba),3))
print('ROC AUC на тестовом наборе', round(metrics.roc_auc_score(y_valid, y_valid_LR_pred_proba),3))

print('Основные метрики на тестовом наборе:')
print(metrics.classification_report(y_valid,y_valid_LR_pred))

# time: 3m 5s

ROC AUC на обучающем наборе 0.602
ROC AUC на тестовом наборе 0.604
Основные метрики на тестовом наборе:
              precision    recall  f1-score   support

           0       0.97      0.57      0.72     68747
           1       0.05      0.58      0.09      2503

    accuracy                           0.57     71250
   macro avg       0.51      0.57      0.40     71250
weighted avg       0.94      0.57      0.69     71250



##### <span style="color:MediumSlateBlue">Анализ влияния scaler преобразования на качество и скорость схождения модели</span>

In [1137]:
# формируем список из необходимых scaler
scalers = [MinMaxScaler(),RobustScaler() ,StandardScaler()]

# сформируем списко для заполнения данными результатов анализа
scalers_data = []

# установим ограничение на время обучения модели в 600 секунд (10 минут)
time_out = 600

for scaler in scalers:
        # для того чтобы следить за выполнением цикла введем индикатор
        print('current scaler: ', scaler)

         # сформируем список для заполнения данными текушего scaler
        current_scaler_data = [scaler]
        
        # выполним scaler преобразование
        X_train_s_balanced = scaler.fit_transform(X_train_balanced[list_ncorr_features])
        X_train_s = scaler.transform(X_train[list_ncorr_features])
        X_valid_s = scaler.transform(X_valid[list_ncorr_features])

        try:
                # для модуля func_time_out упакуем обучение модели в функцию try_func
                def try_func():
                        logistic_regression = linear_model.LogisticRegression(random_state=42, max_iter=10000)
                        return logistic_regression.fit(X_train_s_balanced,y_train_balanced)
                    
                # фиксируем время начала
                start_time = time.time()
                
                # запускаем обучение модели с ограничением по времени
                logistic_regression = func_timeout.func_timeout(time_out, try_func)
                
                # фиксируем время окончания обучения
                end_time = time.time()
                
                # запишем время обучения модели
                current_scaler_data.append(round(end_time-start_time))

                # Делаем предсказание для обучающей и валидационной выборки
                y_valid_lr_pred = logistic_regression.predict(X_valid_s)
                
                # для метрик ROC AUC делаем предсказание модели для обучающей и валидационной выборки  
                # в виде вероятности принадлежности к классу 1 
                y_train_lr_pred_proba = logistic_regression.predict_proba(X_train_s)[:,1]
                y_valid_lr_pred_proba = logistic_regression.predict_proba(X_valid_s)[:,1]

                #Считаем метрики ROC AUC yна обуающем и валидационном наборе и добавляем их в спискок
                current_scaler_data.append(round(metrics.roc_auc_score(y_train, y_train_lr_pred_proba),3))
                current_scaler_data.append(round(metrics.roc_auc_score(y_valid, y_valid_lr_pred_proba),3))

                #Считаем метрики для класса 0 на валидационном наборе и добавляем их в список
                current_scaler_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))
                current_scaler_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))


                #Считаем метрики для класса 1 на валидационном набопе и добавляем их в список
                current_scaler_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))
                current_scaler_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))

                # добавляем полученные данные в список scalers_data
                scalers_data.append(current_scaler_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                scaler_pd =pd.DataFrame(
                        columns=['scaler','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = scalers_data)
                # сохраняем dataframe
                scaler_pd.to_csv('data_recovery/scaler_pd.csv',index=False)
               
                # очистим output от прошедшей итерации
                clear_output()

        except func_timeout.FunctionTimedOut:
                # если время обучения привышает лимит
                # запишем в current_scaler_data соотвествующую данные
                current_scaler_data = [scaler,'>30m',0,0,0,0,0,0]
                # добавляем полученные данные в список scalers_data
                scalers_data.append(current_scaler_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                scaler_pd =pd.DataFrame(
                        columns=['scaler','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = scalers_data)
                # сохраняем dataframe
                scaler_pd.to_csv('data_recovery/scaler_pd.csv',index=False)
                
                # очистим output от прошедшей итерации
                clear_output()
                # переходим к следующему scaler
                pass
# очистим output
clear_output()

# сформируем данные соотвествующие лучщему ROC AUC на валидацинном наборе
best_roc_valid_data = scaler_pd[scaler_pd['roc_valid']==scaler_pd['roc_valid'].max()]

# выведем лучший результат на валидационном наборе
print('result:')
print('best scaler on valid:',best_roc_valid_data.iloc[0]['scaler'])
print('ROC AUC on train:', best_roc_valid_data.iloc[0]['roc_train'])
print('ROC AUC on valid:', best_roc_valid_data.iloc[0]['roc_valid'])
print('Time fit for best scaler:', best_roc_valid_data.iloc[0]['time_fit'],' seconds')

# выведем полученный dataframe
scaler_pd

# time: 

result:
best scaler on valid: MinMaxScaler()
ROC AUC on train: 0.602
ROC AUC on valid: 0.604
Time fit for best scaler: 0  seconds


scaler  time_fit  roc_train  roc_valid  recall_0  precision_0  \
0    MinMaxScaler()         0      0.602      0.604     0.555        0.974   
1    RobustScaler()         0      0.602      0.604     0.567        0.974   
2  StandardScaler()         0      0.602      0.604     0.566        0.974   

   recall_1  precision_1  
0     0.594        0.046  
1     0.582        0.047  
2     0.584        0.047

##### <span style="color:MediumSlateBlue"> Анализ влияния solver оптимизатора на качество и скорость обучения модели</span>

Проверим качество и скорость сходимости модели при разных solver  
Проверку осуществим через цикл  
Чтобы модель не сходилась бесконечно с помощью модуля func_timeout  
поставим ограничение времени схождения в 10 минут

In [1138]:
# подготовим данные для обучения модели

# обьявим scaler
scaler = StandardScaler()
# выполним scaler преобразование
X_train_s_balanced = scaler.fit_transform(X_train_balanced[list_ncorr_features])
X_train_s = scaler.transform(X_train[list_ncorr_features])
X_valid_s = scaler.transform(X_valid[list_ncorr_features])

# time: 10s

In [1139]:
# Зададим список solvers
solvers_list = ['lbfgs', 'liblinear', 'newton-cg', 'newton-cholesky', 'sag', 'saga']

# сформируем список для заполнения
solvers_data = []

# установим ограничение на время обучения модели в 180 секунд (3 минут)
time_out = 180

for solver in solvers_list:
        # для того чтобы следить за выполнением цикла введем индикатор
        print('current solver: ', solver)

         # сформируем список для заполнения данными текушего solver
        current_solver_data = [solver]
        
        try:
                # для модуля func_time_out упакуем обучение модели в функцию try_func
                def try_func():
                        logistic_regression = linear_model.LogisticRegression(solver= solver,
                                                                  random_state=42, 
                                                                  max_iter=10000)
                        return logistic_regression.fit(X_train_s_balanced,y_train_balanced)
                    
                # фиксируем время начала
                start_time = time.time()
                
                # запускаем обучение модели с ограничением по времени
                logistic_regression = func_timeout.func_timeout(time_out, try_func)
                
                # фиксируем время окончания обучения
                end_time = time.time()
                
                # запишем время обучения модели
                current_solver_data.append(round(end_time-start_time))

                # Делаем предсказание для обучающей и валидационной выборки
                y_valid_lr_pred = logistic_regression.predict(X_valid_s)
                
                # для метрик ROC AUC делаем предсказание модели для обучающей и валидационной выборки  
                # в виде вероятности принадлежности к классу 1 
                y_train_lr_pred_proba = logistic_regression.predict_proba(X_train_s)[:,1]
                y_valid_lr_pred_proba = logistic_regression.predict_proba(X_valid_s)[:,1]

                #Считаем метрики ROC AUC yна обуающем и валидационном наборе и добавляем их в спискок
                current_solver_data.append(round(metrics.roc_auc_score(y_train, y_train_lr_pred_proba),3))
                current_solver_data.append(round(metrics.roc_auc_score(y_valid, y_valid_lr_pred_proba),3))

                #Считаем метрики для класса 0 на валидационном наборе и добавляем их в список
                current_solver_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))
                current_solver_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[0],3))


                #Считаем метрики для класса 1 на валидационном набопе и добавляем их в список
                current_solver_data.append(round(metrics.recall_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))
                current_solver_data.append(round(metrics.precision_score(y_valid, y_valid_lr_pred,average=None,zero_division=0)[1],3))

                # запишем данные полученные на одной итерации
                solvers_data.append(current_solver_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                solvers_pd =pd.DataFrame(
                        columns=['solver','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = solvers_data)
                # сохраняем dataframe
                solvers_pd.to_csv('data_recovery/solvers_pd.csv',index=False)
               
                # очистим output от прошедшей итерации
                clear_output()

        except func_timeout.FunctionTimedOut:
                # если время обучения привышает лимит
                # запишем в current_solver_data соотвествующую данные
                current_solver_data = [solver,'>3m',0,0,0,0,0,0]
                # добавляем полученные данные в список solvers_data
                solvers_data.append(current_solver_data)

                # чтобы подстраховаться на случай ошибки : "The Kernel crashed while executing code"
                # сохраним в локальную папку удачную итерацию
                # для этого из полученных данных сформируем dataframe
                # из полученных данных сформируем dataframe
                solvers_pd =pd.DataFrame(
                        columns=['solver','time_fit',
                                 'roc_train','roc_valid', 
                                 'recall_0','precision_0',
                                 'recall_1','precision_1'],
                        data = solvers_data)
                # сохраняем dataframe
                solvers_pd.to_csv('data_recovery/solvers_pd.csv',index=False)
                
                # очистим output от прошедшей итерации
                clear_output()
                # переходим к следующему solver
                pass
# очистим output
clear_output()

# сформируем данные соотвествующие лучщему ROC AUC на валидацинном наборе
best_roc_valid_data = solvers_pd[solvers_pd['roc_valid']==solvers_pd['roc_valid'].max()]

# выведем лучший результат на валидационном наборе
print('result:')
print('best solver on valid:',best_roc_valid_data.iloc[0]['solver'])
print('ROC AUC on train:', best_roc_valid_data.iloc[0]['roc_train'])
print('ROC AUC on valid:', best_roc_valid_data.iloc[0]['roc_valid'])
print('Time fit for best solver:', best_roc_valid_data.iloc[0]['time_fit'],' seconds')

# выведем полученный dataframe
solvers_pd

# time: 2m 35s

result:
best solver on valid: lbfgs
ROC AUC on train: 0.602
ROC AUC on valid: 0.604
Time fit for best solver: 0  seconds


solver  time_fit  roc_train  roc_valid  recall_0  precision_0  \
0            lbfgs         0      0.602      0.604     0.566        0.974   
1        liblinear         0      0.602      0.604     0.566        0.974   
2        newton-cg         0      0.602      0.604     0.566        0.974   
3  newton-cholesky         0      0.602      0.604     0.566        0.974   
4              sag         0      0.602      0.604     0.566        0.974   
5             saga         0      0.602      0.604     0.566        0.974   

   recall_1  precision_1  
0     0.584        0.047  
1     0.584        0.047  
2     0.584        0.047  
3     0.584        0.047  
4     0.584        0.047  
5     0.584        0.047

##### <span style="color:MediumSlateBlue">Подбор гиперпараметров модели</span>

In [1802]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'service'
count_features = dict_spaces[feature_space]

# для работы функции corr_transform_to_force
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()

# для выбора sceler преобразвания нам понадобится словарь
dict_scalers ={
    'MinMaxScaler': MinMaxScaler(),
    'RobustScaler':RobustScaler(),
    'StandardScaler':StandardScaler()}

# настроим оптимизацию гипер параметров
def optuna_lg(trial):
  # задаем пространства поиска гиперпараметров
  solver = trial.suggest_categorical("solver", ['lbfgs', 'liblinear', 'newton-cg', 'newton-cholesky'])
  C = trial.suggest_float('C',0.01,1)
  class_0_weight = trial.suggest_float('class_0_weight',0.2,0.6)
  class_1_weight = trial.suggest_float('class_1_weight',0.2,0.6)
  threshold = trial.suggest_float('threshold',0.6,1)
  class_1_percent = trial.suggest_float('class_1_percent',0.01,0.3)
  scaler = trial.suggest_categorical("scaler", ['MinMaxScaler','RobustScaler','StandardScaler'])
  random_state = trial.suggest_int('random_state', 1, 1000000)


  # создаем модель
  optuna_log_reg = linear_model.LogisticRegression(
      solver=solver,
      C=C,
      class_weight={0:class_0_weight,1:class_1_weight},
      random_state=random_state,
      max_iter=10000)

  # с помощью функции corr_transform_to_force получим
  # список не коррелируемых признаков
  list_ncorr_features = corr_transform_to_force(corr_matrix,threshold=threshold)[1]

  # обьявим scaler
  scaler = dict_scalers[scaler]

  # сформируем данные для анализа сбалансированности обучающих данных
  X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
  y_train_pd = pd.read_csv('target/target_train.csv')

  # поготовим данные y_train_pd к работе с функцией class_1_percent_samples
  y_train_pd.set_index('id',drop=False,inplace=True)

  # подготовим данные для обучения модели
  # с помощью функции class_1_percent_samples зададим долю 
  # класса 1
  list_c1_percent_id = class_1_percent_samples(y_train_pd,class_1_percent,random_state=random_state)[:1000000]

  # подготовим данные для обучения
  X_train_s_balanced = scaler.fit_transform(X_train_pd.loc[list_c1_percent_id])
  y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

  # освободим память от "тяжелых" и ненужных файлов
  del X_train_pd, y_train_pd
  gc.collect()

  # я не воспользовался параметром timeout метода optimize потому, что  
  # optimize отставливает поиск параметров, если время обучения 
  # превышает timeout. Мне нужно чтобы поиск параметров продолжился.
  try:
    # для модуля func_time_out упакуем обучение модели в функцию try_func
    def try_func():
            return optuna_log_reg.fit(X_train_s_balanced, y_train_balanced)
    # обучаем модель с ограничением по времени 10 минут (600 секунд)
    optuna_log_reg = func_timeout.func_timeout(600, try_func)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train_s_balanced, y_train_balanced
    gc.collect()

    # загружаем тестовые наборы
    # сформируем данные для анализа сбалансированности обучающих данных
    X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
    X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()[list_ncorr_features]
    y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
    y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

    # подготовим данные для проверки модели
    X_train_s = scaler.transform(X_train)
    X_valid_s = scaler.transform(X_valid)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train, X_valid
    gc.collect()

    # делаем предсказание на обучающем и валидационном наборе и считаем метрики
    roc_train = metrics.roc_auc_score(y_train, optuna_log_reg.predict_proba(X_train_s)[:,1])
    roc_valid = metrics.roc_auc_score(y_valid, optuna_log_reg.predict_proba(X_valid_s)[:,1])
    f1_score = metrics.f1_score(y_valid, optuna_log_reg.predict(X_valid_s))
    recall_1 = metrics.recall_score(y_valid, optuna_log_reg.predict(X_valid_s),average=None,zero_division=0)[1]
    precision_1 = metrics.precision_score(y_valid, optuna_log_reg.predict(X_valid_s),average=None,zero_division=0)[1]

    # удаляем крупные файлы чтобы высвободить память 
    del X_train_s, X_valid_s, y_train, y_valid
    gc.collect()

  except func_timeout.FunctionTimedOut:
    # удаляем крупные файлы чтобы высвободить память 
    del X_train_s_balanced, y_train_balanced
    gc.collect()
    
    # фиксируем пустые значения метрик
    roc_train = 0
    roc_valid = 0
    f1_score = 0
    recall_1 = 0
    precision_1 = 0
    pass

  return roc_train, roc_valid, f1_score, recall_1, precision_1

In [1803]:
# cоздаем объект исследования
# чтобы модель не переобучалась минимизируем roc_train 
# и максимизируем roc_valid
optuna_study_lg = optuna.create_study(study_name='LogisticRegression_'+feature_space+'_stat', 
                               directions=['maximize','maximize','maximize','maximize','maximize'], 
                               sampler=optuna.samplers.TPESampler(),
                               pruner='Hyperband',
                               storage='sqlite:///optuna_studies.db',
                               load_if_exists=True)
# optuna.delete_study(study_name='LogisticRegression_'+feature_space+'_stat', storage='sqlite:///optuna_studies.db')

[I 2025-04-19 15:11:56,140] Using an existing study with name 'LogisticRegression_service_stat' instead of creating a new one.


In [1142]:
# ищем лучшую комбинацию гиперпараметров n_trials раз
optuna_study_lg.optimize(optuna_lg, n_trials=300)

[I 2025-04-18 08:23:36,234] Trial 0 finished with values: [0.6021125008160485, 0.6026540011122324, 0.0, 0.0, 0.0] and parameters: {'solver': 'newton-cg', 'C': 0.39575961741232585, 'class_0_weight': 0.2770656521656217, 'class_1_weight': 0.21197785674045916, 'threshold': 0.6868821855539667, 'class_1_percent': 0.08677817659441603, 'scaler': 'MinMaxScaler', 'random_state': 107203}.
[I 2025-04-18 08:23:41,601] Trial 1 finished with values: [0.6071821975004567, 0.6052053898217973, 0.052214452214452214, 0.044746304434678384, 0.06267487409065473] and parameters: {'solver': 'newton-cholesky', 'C': 0.9489408328794385, 'class_0_weight': 0.3179486160223205, 'class_1_weight': 0.5922158886973573, 'threshold': 0.7734754799383283, 'class_1_percent': 0.2373736821726138, 'scaler': 'MinMaxScaler', 'random_state': 562000}.
[I 2025-04-18 08:23:47,091] Trial 2 finished with values: [0.6024975526653908, 0.6027754722901039, 0.0, 0.0, 0.0] and parameters: {'solver': 'newton-cholesky', 'C': 0.36892837591375527,

In [1804]:
# из полученного результат соврмируем Data Frame
optuna_study_lg_pd = optuna_study_lg.trials_dataframe().dropna()
# переименуем столбы
optuna_study_lg_pd.rename(columns={
    'values_0': 'roc_train',
    'values_1': 'roc_valid',
    'values_2': 'f1_score',
    'values_3': 'recall_1',
    'values_4': 'precision_1'
},inplace=True)
# Выделим время потраченное на обучение модели
optuna_study_lg_pd.tail()

number  roc_train  roc_valid  f1_score  recall_1  precision_1  \
295     295   0.619928   0.621775  0.098426  0.274870     0.059946   
296     296   0.621778   0.623714  0.088498  0.651219     0.047475   
297     297   0.616523   0.616479  0.002318  0.001199     0.035294   
298     298   0.618664   0.618869  0.003086  0.001598     0.044944   
299     299   0.614872   0.615688  0.063692  0.060727     0.066960   

                datetime_start          datetime_complete  \
295 2025-04-18 08:55:36.632300 2025-04-18 08:55:43.997827   
296 2025-04-18 08:55:44.003696 2025-04-18 08:55:53.381809   
297 2025-04-18 08:55:53.387198 2025-04-18 08:56:00.380628   
298 2025-04-18 08:56:00.385575 2025-04-18 08:56:07.897835   
299 2025-04-18 08:56:07.902791 2025-04-18 08:56:14.928714   

                  duration  params_C  params_class_0_weight  \
295 0 days 00:00:07.365527  0.881945               0.241842   
296 0 days 00:00:09.378113  0.518018               0.215085   
297 0 days 00:00:06.993430  0.513328               0.214121   
298 0 days 00:00:07.512260  0.538470               0.583252   
299 0 days 00:00:07.025923  0.507105               0.250254   

     params_class_1_percent  params_class_1_weight  params_random_state  \
295                0.299859               0.417528               273454   
296                0.287401               0.565430               328848   
297                0.157947               0.300664               355534   
298                0.212367               0.427329                91366   
299                0.287256               0.348085               383172   

    params_scaler    params_solver  params_threshold     state  
295  RobustScaler            lbfgs          0.984231  COMPLETE  
296  RobustScaler            lbfgs          0.999422  COMPLETE  
297  MinMaxScaler  newton-cholesky          0.976555  COMPLETE  
298  RobustScaler        liblinear          0.957679  COMPLETE  
299  RobustScaler            lbfgs          0.835534  COMPLETE

In [1805]:
# покаждем статистику обучения
print('Максимальное значение метрики ROC AUC на валидационном наборе:',round(optuna_study_lg_pd['roc_valid'].max(),3))
print('Среднее значение метрики ROC AUC на валидационном наборе:',round(optuna_study_lg_pd['roc_valid'].mean(),3))
print('Максимальное значение метрики f1_score на валидационном наборе:',round(optuna_study_lg_pd['f1_score'].max(),3))
print('Среднее значение метрики f1_score на валидационном наборе:',round(optuna_study_lg_pd['f1_score'].mean(),3))
print('Максимальное значение метрики recall_1 на валидационном наборе:',round(optuna_study_lg_pd['recall_1'].max(),3))
print('Среднее значение метрики recall_1 на валидационном наборе:',round(optuna_study_lg_pd['recall_1'].mean(),3))
print('Максимальное значение метрики precision_1 на валидационном наборе:',round(optuna_study_lg_pd['precision_1'].max(),3))
print('Среднее значение метрики precision_1 на валидационном наборе:',round(optuna_study_lg_pd['precision_1'].mean(),3))

Максимальное значение метрики ROC AUC на валидационном наборе: 0.624
Среднее значение метрики ROC AUC на валидационном наборе: 0.617
Максимальное значение метрики f1_score на валидационном наборе: 0.102
Среднее значение метрики f1_score на валидационном наборе: 0.069
Максимальное значение метрики recall_1 на валидационном наборе: 0.724
Среднее значение метрики recall_1 на валидационном наборе: 0.241
Максимальное значение метрики precision_1 на валидационном наборе: 0.088
Среднее значение метрики precision_1 на валидационном наборе: 0.054


In [1807]:
# Визуализируем метрики полученные при optuna оптимизации
fig = px.scatter(
    data_frame=optuna_study_lg_pd[(optuna_study_lg_pd['roc_valid']>0.9999*optuna_study_lg_pd['roc_valid'].max())],
    x='number', #ось абсцисс
    y=['roc_train','roc_valid','recall_1','precision_1','f1_score'], #ось ординат
)
fig.update_layout(
    title ={
        'text':'Зависимость качества модели от trials optuna', # Имя рабочей плоскости
        'font':{'size':35,'family':"Times New Roman"}, # размер и стиль написания имени рабочей плоскости
        'x':0.5, # Смешение имени по оси "x" на половину рабочей плоскости
        },
    height =800,# Высота рабочей плоскости
    width = 1350, # Ширина рабочей плоскости
    bargap=0.2, # Добавил расстояния между столбами гистограммы
    xaxis_title='trials optuna',
    yaxis_title='Величина метрики')
fig.update_xaxes(showspikes=True)
fig.update_yaxes(showspikes=True)

fig.show()

<span style="color:Blue">

Вывод:  

Их всех выбираем точку $number =296$.   
В этой точке самые оптимальные значения $recall$ и $precision$.  
Посмотрим каким значениям гиперпараметров соотвествует выбранная точка.

In [1808]:
# определим номер лучшге варианта
best_optuna_number = 296

# сформируем словарь лучших гипирпарметров RandomForestClassifier
best_param_lr = {
    'solver' : optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_solver'].iloc[0],
    'C' : round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_C'].iloc[0],3),
    'class_weight' : {0:round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_class_0_weight'].iloc[0],3),
                      1:round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_class_1_weight'].iloc[0],3)},
    }

# создадим перменные
best_threshold = optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_threshold'].iloc[0]
best_scaler = optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_scaler'].iloc[0]
best_class_1_percent = optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_class_1_percent'].iloc[0]
best_random_state = optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['params_random_state'].iloc[0]

# Выведем принятые наилучшие праметры
print('best solver:',best_param_lr['solver'])
print('best C:',best_param_lr['C'])
print('best class 0 weight:',best_param_lr['class_weight'][0])
print('best class 1 weight:',best_param_lr['class_weight'][1])

print('best class 1 percent:',round(best_class_1_percent,3))
print('best scaler:',best_scaler)
print('best threshold:',round(best_threshold,3))
print('best best random state:',best_random_state)
print('time for best train:',round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['duration'].iloc[0].seconds/60),'minutes')

print()
print('ROC AUC на обучающем наборе:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['roc_train'].iloc[0],3))
print('ROC AUC на валидационном наборе:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['roc_valid'].iloc[0],3))
print('precision класса 1:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['precision_1'].iloc[0],3))
print('recall класса 1:', round(optuna_study_lg_pd[optuna_study_lg_pd['number']==best_optuna_number]['recall_1'].iloc[0],3))


best solver: lbfgs
best C: 0.518
best class 0 weight: 0.215
best class 1 weight: 0.565
best class 1 percent: 0.287
best scaler: RobustScaler
best threshold: 0.999
best best random state: 328848
time for best train: 0 minutes

ROC AUC на обучающем наборе: 0.622
ROC AUC на валидационном наборе: 0.624
precision класса 1: 0.047
recall класса 1: 0.651


##### <span style="color:MediumSlateBlue">Обучение модели с лучшими параметрами</span>

In [1809]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'service'
count_features = dict_spaces[feature_space]

# для работы функции corr_transform_to_force
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()

# подготовим данные
# для выбора sceler преобразвания нам понадобится словарь
dict_scalers ={
    'MinMaxScaler': MinMaxScaler(),
    'RobustScaler':RobustScaler(),
    'StandardScaler':StandardScaler(),
}

# с помощью функции corr_transform_to_force получим
# список не коррелируемых признаков
list_ncorr_features = corr_transform_to_force(corr_matrix,threshold=best_threshold)[1]

# обьявим scaler
scaler = dict_scalers[best_scaler]

# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
y_train_pd = pd.read_csv('target/target_train.csv')

# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)

# подготовим данные для обучения модели
# с помощью функции class_1_percent_samples зададим долю 
# класса 1
list_c1_percent_id = class_1_percent_samples(y_train_pd,best_class_1_percent,random_state=best_random_state)[:1000000]

# подготовим данные для обучения
X_train_s_balanced = scaler.fit_transform(X_train_pd.loc[list_c1_percent_id])
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag'].to_numpy()

# освободим память от "тяжелых" и ненужных файлов
del X_train_pd, y_train_pd
gc.collect()


# обучаем модель LogisticRegression с наилучшеми параметрами
logistic_regression = linear_model.LogisticRegression(
        **best_param_lr,
        random_state=42,
        max_iter=10000)
logistic_regression.fit(X_train_s_balanced, y_train_balanced)

# удаляем крупные файлы чтобы высвободить память 
del X_train_s_balanced, y_train_balanced
gc.collect()

# загружаем тестовые наборы
# сформируем данные для анализа сбалансированности обучающих данных
X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()[list_ncorr_features]
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

# подготовим данные для проверки модели
X_train_s = scaler.transform(X_train)
X_valid_s = scaler.transform(X_valid)

# удаляем крупные файлы чтобы высвободить память 
del X_train, X_valid
gc.collect()

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_lr_pred_proba = logistic_regression.predict_proba(X_train_s)[:,1]
y_valid_lr_pred_proba = logistic_regression.predict_proba(X_valid_s)[:,1]

# Делаем предсказание для валидационной выборки
y_valid_lr_pred = logistic_regression.predict(X_valid_s)

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_lr_pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_lr_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_lr_pred,zero_division=0))

# time: 2m 30s

ROC AUC на обучающем наборе 0.622
ROC AUC на валидационном наборе 0.624
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.98      0.52      0.68     68747
           1       0.05      0.65      0.09      2503

    accuracy                           0.53     71250
   macro avg       0.51      0.59      0.38     71250
weighted avg       0.94      0.53      0.66     71250



#### <span style="color:MediumBlue">Построение модели Random Forest Classifier</span>

##### <span style="color:MediumSlateBlue">Формирование данных для обучения</span>

Анализ исходных данных, в частности target, показал что представленные данные   
имееют перекос: 96% клиентов у которых не случился дефолт (flag = 0),    
против 4 % - для которых произошел дефолт (flag = 1).  
С помощью функции class_1_percent_samples, сформируем сбаланисрованную выборку  
для обучения моделей.
За основу сбалансировных данных возьмем данные клиентов с дефолтом  
и к ним будем добирать необходимое количество клиентов до сбалансированности. 


Функция class_1_percent_samples принемает две переменные:
- target_data - массив с id и целевой переменной
- class_1_percent - процент класса 1 в результирующем массиве

In [1160]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'service'
count_features = dict_spaces[feature_space]

In [1161]:
# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

In [1162]:
# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)
y_train_pd.head(4)

id  flag
id                    
1825800  1825800     0
2166483  2166483     0
2534345  2534345     0
1803283  1803283     0

In [1163]:
# взглянем на сблансиорованность данных в y_train
y_train_pd['flag'].value_counts(normalize=True)

flag
0    0.964242
1    0.035758
Name: proportion, dtype: float64

In [1164]:
# сбалансируем данные в y_train_pd
list_c1_percent_id = class_1_percent_samples(y_train_pd,0.5)
# list_c1_percent_features - список 'id' из y_train_pd соотвествующих  
# заданному проценту класса 1
len(list_c1_percent_id)

45860

In [1165]:
# проверим сбалансированность полученного y_train
y_train_pd.loc[list_c1_percent_id]['flag'].value_counts(normalize=True)

flag
1    0.5
0    0.5
Name: proportion, dtype: float64

В отличие от данных в *transform_data_torow*, где модели показываеются последние N  
операций клиента, в данные в *transform_data_stat* сфомированы из различных статистических   
характеристик ряда определяющего клиентскую историю в банке. 

Соотвественно, если в данных *transform_data_torow* была сильная корреляция между признаками,  
то я не смог бы ее убрать, иначе потярется смысл "показать последовательный ряд в историии клиента".  
Признаки в *transform_data_stat* не имеют такой особенности. Поэтому, необходимо проанализировать  
данные в *transform_data_stat* и, в случае сильной коррреляции признаков, устранить ее.

In [1166]:
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()
corr_matrix.shape

(69, 69)

In [1167]:
# с помощью функции corr_transrom_to_power получим
# силу корреляции матрицы и список не коррелируемых признаков

# для начального анализа зададим порог силы корреляции, при котором признаки 
# будут отнесены к "сильно скоррелированными" равным 0.6
ncorr_matrix,list_ncorr_features,corr_power =corr_transform_to_force(corr_matrix,threshold=0.6)

# Выведем результаты преобразования
print('Исходное количество признаков: ', corr_matrix.shape[0])
print('Количество не коррелируемых признаков: ', len(list_ncorr_features))
# сила корреляции признаков
print('Отношение коррелируемых исходному количеству признаков (сила корреляции): ',corr_power)

Исходное количество признаков:  69
Количество не коррелируемых признаков:  26
Отношение коррелируемых исходному количеству признаков (сила корреляции):  0.623


In [1168]:
# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']
# сформируем данные для проверики модели
# сформируем данные для анализа сбалансированности обучающих данных
X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()
y_train = pd.read_csv('target/target_train.csv')['flag']
X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()
y_valid = pd.read_csv('target/target_valid.csv')['flag']

In [1169]:
# посмотрим на структуру данных в X_train_balanced
X_train_balanced.head(4)

f1   f2   f3   f4   f5   f6   f7   f8   f9  f10  ...  f60  f61  \
id                                                          ...             
2335465  17.0  0.0  1.0  1.0  1.0  1.0  1.0  0.0  0.0  1.0  ...  0.0  1.0   
390270    6.0  0.0  1.0  1.0  1.0  1.0  1.0  0.0  0.0  1.0  ...  0.0  1.0   
2494034  14.0  0.0  1.0  1.0  1.0  1.0  1.0  0.0  0.0  1.0  ...  0.0  1.0   
2018674  15.0  0.0  1.0  1.0  1.0  1.0  1.0  0.0  0.0  1.0  ...  0.0  1.0   

         f62  f63  f64  f65  f66  f67  f68  f69  
id                                               
2335465  1.0  1.0  1.0  1.0  1.0  1.0  0.0  1.0  
390270   1.0  1.0  1.0  1.0  1.0  1.0  0.0  1.0  
2494034  1.0  1.0  1.0  1.0  1.0  1.0  0.0  1.0  
2018674  1.0  1.0  1.0  1.0  1.0  1.0  0.0  1.0  

[4 rows x 69 columns]

In [1170]:
# посмотрим на структуру данных в y_train_balanced
y_train_balanced.head(4)

id
2335465    1
390270     1
2494034    1
2018674    1
Name: flag, dtype: int64

In [1171]:
# проверим что выборки действительно совпадают по id
X_train_balanced.index.to_list() == y_train_balanced.index.to_list()

True

##### <span style="color:MediumSlateBlue">Baseline обучение модели RandomForestClassifier</span>

In [1172]:
# обучаем модель логистической регрессии
# чтобы модель пыталась найти связь во всех признаках
random_forest = RandomForestClassifier(random_state=42, n_jobs=-1)
random_forest.fit(X_train_balanced[list_ncorr_features],y_train_balanced)

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_rf__pred_proba = random_forest.predict_proba(X_train[list_ncorr_features])[:,1]
y_valid_rf_pred_proba = random_forest.predict_proba(X_valid[list_ncorr_features])[:,1]

# Делаем предсказание для валидационной выборки
y_valid_rf_pred = random_forest.predict(X_valid[list_ncorr_features])

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_rf__pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_rf_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_rf_pred))

# time: 17s

ROC AUC на обучающем наборе 0.742
ROC AUC на валидационном наборе 0.603
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.97      0.54      0.69     68747
           1       0.05      0.62      0.09      2503

    accuracy                           0.54     71250
   macro avg       0.51      0.58      0.39     71250
weighted avg       0.94      0.54      0.67     71250



##### <span style="color:MediumSlateBlue">Подбор гиперпараметров модели</span>

In [1810]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'service'
count_features = dict_spaces[feature_space]

# для работы функции corr_transform_to_force
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()

# настроим оптимизацию гипер параметров
def optuna_rf(trial):
  # задаем пространства поиска гиперпараметров
  # задаем пространства поиска гиперпараметров
  n_estimators = trial.suggest_int('n_estimators', 40, 100,step = 5)
  criterion = trial.suggest_categorical('criterion',['gini', 'entropy', 'log_loss'])
  max_depth = trial.suggest_int('max_depth', 10, 30,step = 1)
  min_samples_split = trial.suggest_int('min_samples_split', 5, 15,step = 1)
  min_samples_leaf = trial.suggest_int('min_samples_leaf', 5, 15,step = 1)
  max_features = trial.suggest_float('max_features',0.4,0.8)
  max_samples = trial.suggest_float('max_samples',0.4,0.8)
  class_0_weight = trial.suggest_float('class_0_weight',0.1,1)
  class_1_weight = trial.suggest_float('class_1_weight',0.1,1)
  threshold = trial.suggest_float('threshold',0.4,0.8)
  class_1_percent = trial.suggest_float('class_1_percent',0.01,0.5)
  random_state = trial.suggest_int('random_state', 1, 1000000)


  # создаем модель
  optuna_random_forest = RandomForestClassifier(
      n_estimators = n_estimators, 
      criterion = criterion,
      max_depth = max_depth,
      min_samples_split = min_samples_split,  
      min_samples_leaf = min_samples_leaf,
      max_features=max_features,
      max_samples=max_samples,
      class_weight={0:class_0_weight,1:class_1_weight},
      n_jobs=-1,
      random_state=42)

  # с помощью функции corr_transform_to_force получим
  # список не коррелируемых признаков
  list_ncorr_features = corr_transform_to_force(corr_matrix,threshold=threshold)[1]

  # сформируем данные для анализа сбалансированности обучающих данных
  X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
  y_train_pd = pd.read_csv('target/target_train.csv')

  # поготовим данные y_train_pd к работе с функцией class_1_percent_samples
  y_train_pd.set_index('id',drop=False,inplace=True)

  # подготовим данные для обучения модели
  # с помощью функции class_1_percent_samples зададим долю 
  # класса 1
  list_c1_percent_id = class_1_percent_samples(y_train_pd,class_1_percent,random_state=random_state)[:1000000]

  # подготовим данные для обучения
  X_train_balanced = X_train_pd.loc[list_c1_percent_id]
  y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']

  # освободим память от "тяжелых" и ненужных файлов
  del X_train_pd, y_train_pd
  gc.collect()

  # я не воспользовался параметром timeout метода optimize потому, что  
  # optimize отставливает поиск параметров, если время обучения 
  # превышает timeout. Мне нужно чтобы поиск параметров продолжился.
  try:
    # для модуля func_time_out упакуем обучение модели в функцию try_func
    def try_func():
            return optuna_random_forest.fit(X_train_balanced, y_train_balanced)
    # обучаем модель с ограничением по времени 10 минут (600 секунд)
    optuna_random_forest = func_timeout.func_timeout(600, try_func)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train_balanced, y_train_balanced
    gc.collect()

    # загружаем тестовые наборы
    # сформируем данные для анализа сбалансированности обучающих данных
    X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
    X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()[list_ncorr_features]
    y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
    y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()
    
    # делаем предсказание на обучающем и валидационном наборе
    #Считаем метрики для класса 1 добавляем их в список
    roc_train = metrics.roc_auc_score(y_train, optuna_random_forest.predict_proba(X_train)[:,1])
    roc_valid = metrics.roc_auc_score(y_valid, optuna_random_forest.predict_proba(X_valid)[:,1])
    f1_score = metrics.f1_score(y_valid, optuna_random_forest.predict(X_valid))
    recall_1 = metrics.recall_score(y_valid, optuna_random_forest.predict(X_valid),average=None,zero_division=0)[1]
    precision_1 = metrics.precision_score(y_valid, optuna_random_forest.predict(X_valid),average=None,zero_division=0)[1]

    # удаляем крупные файлы чтобы высвободить память 
    del X_train, X_valid, y_train, y_valid
    gc.collect()

  except func_timeout.FunctionTimedOut:
    # удаляем крупные файлы чтобы высвободить память 
    del X_train_balanced, y_train_balanced
    gc.collect()
    
    # фиксируем пустые значения метрик
    roc_train = 0
    roc_valid = 0
    f1_score = 0
    recall_1 = 0
    precision_1 = 0
    pass

  return roc_train, roc_valid, f1_score, recall_1, precision_1

In [1811]:
# cоздаем объект исследования
optuna_study_rf = optuna.create_study(study_name= 'RandomForestClassifier_'+feature_space+'_stat', 
                               directions=['maximize','maximize','maximize','maximize','maximize'], 
                               sampler=optuna.samplers.TPESampler(),
                               pruner='Hyperband',
                               storage='sqlite:///optuna_studies.db',
                               load_if_exists=True)
# на случай удаления 
# optuna.delete_study(study_name='RandomForestClassifier_'+feature_space+'_stat', storage='sqlite:///optuna_studies.db')

[I 2025-04-19 15:13:24,867] Using an existing study with name 'RandomForestClassifier_service_stat' instead of creating a new one.


In [1175]:
# ищем лучшую комбинацию гиперпараметров n_trials раз
optuna_study_rf.optimize(optuna_rf, n_trials=300)

[I 2025-04-18 08:56:45,846] Trial 4 finished with values: [0.6770890354698016, 0.6326727504576077, 0.04188829787234043, 0.025169796244506593, 0.12475247524752475] and parameters: {'n_estimators': 70, 'criterion': 'log_loss', 'max_depth': 30, 'min_samples_split': 11, 'min_samples_leaf': 12, 'max_features': 0.5289681746502145, 'max_samples': 0.4818508721533268, 'class_0_weight': 0.53266798069535, 'class_1_weight': 0.2462354831048716, 'threshold': 0.710801930278796, 'class_1_percent': 0.3406842149937606, 'random_state': 881812}.
[I 2025-04-18 08:56:50,719] Trial 5 finished with values: [0.6659853686017349, 0.6335645628812127, 0.0947799750579013, 0.10627247303236116, 0.08553054662379421] and parameters: {'n_estimators': 40, 'criterion': 'gini', 'max_depth': 14, 'min_samples_split': 9, 'min_samples_leaf': 12, 'max_features': 0.5036142295682123, 'max_samples': 0.5722249527081037, 'class_0_weight': 0.7528732156298206, 'class_1_weight': 0.819606457749077, 'threshold': 0.44144326071897366, 'cla

In [1812]:
# из полученного результат соврмируем Data Frame
optuna_study_rf_pd = optuna_study_rf.trials_dataframe().dropna()
# переименуем столбы
optuna_study_rf_pd.rename(columns={
    'values_0': 'roc_train',
    'values_1': 'roc_valid',
    'values_2': 'f1_score',
    'values_3': 'recall_1',
    'values_4': 'precision_1'
},inplace=True)
optuna_study_rf_pd.tail()

number  roc_train  roc_valid  f1_score  recall_1  precision_1  \
299     299   0.771539   0.611576  0.000000  0.000000     0.000000   
300     300   0.698982   0.635666  0.002380  0.001199     0.166667   
301     301   0.657234   0.638809  0.104615  0.421095     0.059727   
302     302   0.655833   0.634387  0.091030  0.656013     0.048908   
303     303   0.703143   0.627570  0.092270  0.587295     0.050068   

                datetime_start          datetime_complete  \
299 2025-04-18 09:35:47.213773 2025-04-18 09:36:02.313830   
300 2025-04-18 09:36:02.319824 2025-04-18 09:36:22.361662   
301 2025-04-18 09:36:22.368866 2025-04-18 09:36:31.832644   
302 2025-04-18 09:36:31.838578 2025-04-18 09:36:40.931787   
303 2025-04-18 09:36:40.937748 2025-04-18 09:36:50.979791   

                  duration  params_class_0_weight  ...  params_criterion  \
299 0 days 00:00:15.100057               0.396262  ...              gini   
300 0 days 00:00:20.041838               0.140168  ...              gini   
301 0 days 00:00:09.463778               0.158535  ...          log_loss   
302 0 days 00:00:09.093209               0.849657  ...          log_loss   
303 0 days 00:00:10.042043               0.259120  ...              gini   

     params_max_depth params_max_features  params_max_samples  \
299                25            0.572494            0.779592   
300                13            0.514443            0.791319   
301                10            0.581234            0.485701   
302                11            0.799051            0.750796   
303                29            0.498306            0.760447   

     params_min_samples_leaf  params_min_samples_split  params_n_estimators  \
299                        5                        13                   50   
300                        5                        14                   50   
301                        5                        14                   55   
302                        5                        13                   60   
303                       12                        15                   65   

     params_random_state  params_threshold     state  
299               241827          0.651853  COMPLETE  
300               989431          0.637189  COMPLETE  
301               269992          0.653852  COMPLETE  
302               862648          0.485086  COMPLETE  
303               347312          0.660685  COMPLETE  

[5 rows x 22 columns]

In [1813]:
# покаждем статистику обучения
print('Максимальное значение метрики ROC AUC на валидационном наборе:',round(optuna_study_rf_pd['roc_valid'].max(),3))
print('Среднее значение метрики ROC AUC на валидационном наборе:',round(optuna_study_rf_pd['roc_valid'].mean(),3))
print('Максимальное значение метрики f1_score на валидационном наборе:',round(optuna_study_rf_pd['f1_score'].max(),3))
print('Среднее значение метрики f1_score на валидационном наборе:',round(optuna_study_rf_pd['f1_score'].mean(),3))
print('Максимальное значение метрики recall_1 на валидационном наборе:',round(optuna_study_rf_pd['recall_1'].max(),3))
print('Среднее значение метрики recall_1 на валидационном наборе:',round(optuna_study_rf_pd['recall_1'].mean(),3))
print('Максимальное значение метрики precision_1 на валидационном наборе:',round(optuna_study_rf_pd['precision_1'].max(),3))
print('Среднее значение метрики precision_1 на валидационном наборе:',round(optuna_study_rf_pd['precision_1'].mean(),3))

Максимальное значение метрики ROC AUC на валидационном наборе: 0.641
Среднее значение метрики ROC AUC на валидационном наборе: 0.629
Максимальное значение метрики f1_score на валидационном наборе: 0.112
Среднее значение метрики f1_score на валидационном наборе: 0.073
Максимальное значение метрики recall_1 на валидационном наборе: 0.998
Среднее значение метрики recall_1 на валидационном наборе: 0.358
Максимальное значение метрики precision_1 на валидационном наборе: 1.0
Среднее значение метрики precision_1 на валидационном наборе: 0.089


In [1815]:
# Построим зависимость метрик качества модели от number

fig = px.scatter(
    data_frame=optuna_study_rf_pd[(optuna_study_rf_pd['roc_valid']>=0.9999*optuna_study_rf_pd['roc_valid'].max())],
    x='number', #ось абсцисс
    y=['roc_valid','roc_train','precision_1','recall_1','f1_score'], #ось ординат
)
fig.update_layout(
    title ={
        'text':'Зависимость качества модели от trials optuna', # Имя рабочей плоскости
        'font':{'size':35,'family':"Times New Roman"}, # размер и стиль написания имени рабочей плоскости
        'x':0.5, # Смешение имени по оси "x" на половину рабочей плоскости
        },
    height =800,# Высота рабочей плоскости
    width = 1350, # Ширина рабочей плоскости
    bargap=0.2, # Добавил расстояния между столбами гистограммы
    xaxis_title='trials optuna',
    yaxis_title='Величина параметра')
fig.update_xaxes(showspikes=True)
fig.update_yaxes(showspikes=True)

fig.show()

<span style="color:Blue">

Вывод:  

Их всех выбираем точку $number =20$.   
Не смотря на, то что в этой точке модель подает признаки переобучеености,  
в этой точке оптимальные значения метрик $recall_1$ и $precision_1$, а  
также относительно высокая метрика $ROC AUC$.   
Посмотрим каким значениям гиперпараметров соотвествует выбраннаяточка.

In [1816]:
# определим номер лучшге варианта
best_optuna_number = 20

# сформируем словарь лучших гипирпарметров RandomForestClassifier
best_param_rf = {
    'n_estimators' : int(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_n_estimators'].iloc[0]),
    'criterion': optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_criterion'].iloc[0],
    'max_depth' : int(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_max_depth'].iloc[0]),
    'min_samples_split': int(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_min_samples_split'].iloc[0]),
    'min_samples_leaf' : int(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_min_samples_leaf'].iloc[0]),
    'max_features': optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_max_features'].iloc[0],
    'max_samples' : optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_max_samples'].iloc[0],
    'class_weight' : {0:optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_class_0_weight'].iloc[0],
                      1:optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_class_1_weight'].iloc[0]}
    }

# определим перменные для лучших значений параметров
best_threshold = optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_threshold'].iloc[0]
best_class_1_percent = optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_class_1_percent'].iloc[0]
best_random_state = optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['params_random_state'].iloc[0]


# Выведем принятые наилучшие праметры
print('best n estimators:',best_param_rf['n_estimators'])
print('best criterion:',best_param_rf['criterion'])
print('best max depth:',best_param_rf['max_depth'])
print('best min samples split:',best_param_rf['min_samples_split'])
print('best min samples leaf:',best_param_rf['min_samples_leaf'])
print('best max features(%):',round(best_param_rf['max_features'],3))
print('best max samples(%):',round(best_param_rf['max_samples'],3))
print('best class 0 weight:',round(best_param_rf['class_weight'][0],3))
print('best class 1 weight:',round(best_param_rf['class_weight'][1],3))

print('best class 1 percent:',round(best_class_1_percent,3))
print('best threshold:',round(best_threshold,3))
print('best random state:', best_random_state)
print('time for best train:',round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['duration'].iloc[0].seconds/60),'minutes')

print()
print('ROC AUC на обучающем наборе:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['roc_train'].iloc[0],3))
print('ROC AUC на валидационном наборе:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['roc_valid'].iloc[0],3))
print('precision класса 1:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['precision_1'].iloc[0],3))
print('recall класса 1:', round(optuna_study_rf_pd[optuna_study_rf_pd['number']==best_optuna_number]['recall_1'].iloc[0],3))

best n estimators: 75
best criterion: log_loss
best max depth: 10
best min samples split: 7
best min samples leaf: 11
best max features(%): 0.593
best max samples(%): 0.4
best class 0 weight: 0.64
best class 1 weight: 0.851
best class 1 percent: 0.078
best threshold: 0.685
best random state: 586745
time for best train: 0 minutes

ROC AUC на обучающем наборе: 0.657
ROC AUC на валидационном наборе: 0.641
precision класса 1: 1.0
recall класса 1: 0.0


##### <span style="color:MediumSlateBlue">Обучение модели с лучшими параметрами</span>

In [1817]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'service'
count_features = dict_spaces[feature_space]

# для работы функции corr_transform_to_force
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()

# с помощью функции corr_transform_to_force получим
# список не коррелируемых признаков
list_ncorr_features = corr_transform_to_force(corr_matrix,threshold=best_threshold)[1]

# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
y_train_pd = pd.read_csv('target/target_train.csv')

# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)

# подготовим данные для обучения модели
# с помощью функции class_1_percent_samples зададим долю 
# класса 1
list_c1_percent_id = class_1_percent_samples(y_train_pd,best_class_1_percent,random_state=best_random_state)[:1000000]

# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']

# освободим память от "тяжелых" и ненужных файлов
del X_train_pd, y_train_pd
gc.collect()


# обучаем модель RandomForestClassifier с наилучшеми параметрами
random_forest = RandomForestClassifier(
        **best_param_rf,
        n_jobs=-1,
        random_state=42)
random_forest.fit(X_train_balanced, y_train_balanced)

# удаляем крупные файлы чтобы высвободить память 
del X_train_balanced, y_train_balanced
gc.collect()

# загружаем тестовые наборы
# сформируем данные для анализа сбалансированности обучающих данных
X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()[list_ncorr_features]
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_rf_pred_proba = random_forest.predict_proba(X_train)[:,1]
y_valid_rf_pred_proba = random_forest.predict_proba(X_valid)[:,1]

# Делаем предсказание для валидационной выборки
y_valid_rf_pred = random_forest.predict(X_valid)

# удаляем крупные файлы чтобы высвободить память 
del X_train, X_valid
gc.collect()

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_rf_pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_rf_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_rf_pred,zero_division=0))

# time: 5m 30s

ROC AUC на обучающем наборе 0.657
ROC AUC на валидационном наборе 0.641
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.96      1.00      0.98     68747
           1       1.00      0.00      0.00      2503

    accuracy                           0.96     71250
   macro avg       0.98      0.50      0.49     71250
weighted avg       0.97      0.96      0.95     71250



#### <span style="color:MediumBlue">Построение модели Gradient Boosting Classifier</span>

##### <span style="color:MediumSlateBlue">Формирование данных для обучения</span>

Анализ исходных данных, в частности target, показал что представленные данные   
имееют перекос: 96% клиентов у которых не случился дефолт (flag = 0),    
против 4 % - для которых произошел дефолт (flag = 1).  
С помощью функции class_1_percent_samples, сформируем сбаланисрованную выборку  
для обучения моделей.
За основу сбалансировных данных возьмем данные клиентов с дефолтом  
и к ним будем добирать необходимое количество клиентов до сбалансированности. 


Функция class_1_percent_samples принемает две переменные:
- target_data - массив с id и целевой переменной
- class_1_percent - процент класса 1 в результирующем массиве

In [1192]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'service'
count_features = dict_spaces[feature_space]

In [1193]:
# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()
y_train_pd = pd.read_csv('target/target_train.csv')

In [1194]:
# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)
y_train_pd.head(4)

id  flag
id                    
1825800  1825800     0
2166483  2166483     0
2534345  2534345     0
1803283  1803283     0

In [1195]:
# взглянем на сблансиорованность данных в y_train
y_train_pd['flag'].value_counts(normalize=True)

flag
0    0.964242
1    0.035758
Name: proportion, dtype: float64

In [1196]:
# сбалансируем данные в y_train_pd
list_c1_percent_id = class_1_percent_samples(y_train_pd,0.5)
# list_c1_percent_features - список 'id' из y_train_pd соотвествующих  
# заданному проценту класса 1
len(list_c1_percent_id)

45860

In [1197]:
# проверим сбалансированность полученного y_train
y_train_pd.loc[list_c1_percent_id]['flag'].value_counts(normalize=True)

flag
1    0.5
0    0.5
Name: proportion, dtype: float64

В отличие от данных в *transform_data_torow*, где модели показываеются последние N  
операций клиента, в данные в *transform_data_stat* сфомированы из различных статистических   
характеристик ряда определяющего клиентскую историю в банке. 

Соотвественно, если в данных *transform_data_torow* была сильная корреляция между признаками,  
то я не смог бы ее убрать, иначе потярется смысл "показать последовательный ряд в историии клиента".  
Признаки в *transform_data_stat* не имеют такой особенности. Поэтому, необходимо проанализировать  
данные в *transform_data_stat* и, в случае сильной коррреляции признаков, устранить ее.

In [1198]:
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()
corr_matrix.shape

(69, 69)

In [1199]:
# с помощью функции corr_transrom_to_power получим
# силу корреляции матрицы и список не коррелируемых признаков

# для начального анализа зададим порог силы корреляции, при котором признаки 
# будут отнесены к "сильно скоррелированными" равным 0.6
ncorr_matrix,list_ncorr_features,corr_power =corr_transform_to_force(corr_matrix,threshold=0.6)

# Выведем результаты преобразования
print('Исходное количество признаков: ', corr_matrix.shape[0])
print('Количество не коррелируемых признаков: ', len(list_ncorr_features))
# сила корреляции признаков
print('Отношение коррелируемых исходному количеству признаков (сила корреляции): ',corr_power)

Исходное количество признаков:  69
Количество не коррелируемых признаков:  26
Отношение коррелируемых исходному количеству признаков (сила корреляции):  0.623


In [1200]:
# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']
# сформируем данные для проверики модели
# сформируем данные для анализа сбалансированности обучающих данных
X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()
y_train = pd.read_csv('target/target_train.csv')['flag']
X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()
y_valid = pd.read_csv('target/target_valid.csv')['flag']

In [1201]:
# посмотрим на структуру данных в X_train_balanced
X_train_balanced.head(4)

f1   f2   f3   f4   f5   f6   f7   f8   f9  f10  ...  f60  f61  \
id                                                          ...             
2335465  17.0  0.0  1.0  1.0  1.0  1.0  1.0  0.0  0.0  1.0  ...  0.0  1.0   
390270    6.0  0.0  1.0  1.0  1.0  1.0  1.0  0.0  0.0  1.0  ...  0.0  1.0   
2494034  14.0  0.0  1.0  1.0  1.0  1.0  1.0  0.0  0.0  1.0  ...  0.0  1.0   
2018674  15.0  0.0  1.0  1.0  1.0  1.0  1.0  0.0  0.0  1.0  ...  0.0  1.0   

         f62  f63  f64  f65  f66  f67  f68  f69  
id                                               
2335465  1.0  1.0  1.0  1.0  1.0  1.0  0.0  1.0  
390270   1.0  1.0  1.0  1.0  1.0  1.0  0.0  1.0  
2494034  1.0  1.0  1.0  1.0  1.0  1.0  0.0  1.0  
2018674  1.0  1.0  1.0  1.0  1.0  1.0  0.0  1.0  

[4 rows x 69 columns]

In [1202]:
# посмотрим на структуру данных в y_train_balanced
y_train_balanced.head(4)

id
2335465    1
390270     1
2494034    1
2018674    1
Name: flag, dtype: int64

In [1203]:
# проверим что выборки действительно совпадают по id
X_train_balanced.index.to_list() == y_train_balanced.index.to_list()

True

##### <span style="color:MediumSlateBlue">Baseline обучение модели Hist Gradient Boosting Classifier</span>

In [1204]:
# обучаем модель Gradient Boosting Classifier
gradient_boosting = HistGradientBoostingClassifier(random_state=42)
gradient_boosting.fit(X_train_balanced[list_ncorr_features],y_train_balanced)

# для метрик ROC AUC делаем предсказание модели в виде вероятности
y_train_rf__pred_proba = gradient_boosting.predict_proba(X_train[list_ncorr_features])[:,1]
y_valid_rf_pred_proba = gradient_boosting.predict_proba(X_valid[list_ncorr_features])[:,1]

# Делаем предсказание для валидационной выборки
y_valid_rf_pred = gradient_boosting.predict(X_valid[list_ncorr_features])

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_rf__pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_rf_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_rf_pred))

# time: 30s

ROC AUC на обучающем наборе 0.647
ROC AUC на валидационном наборе 0.636
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.98      0.60      0.74     68747
           1       0.05      0.60      0.09      2503

    accuracy                           0.60     71250
   macro avg       0.51      0.60      0.42     71250
weighted avg       0.94      0.60      0.72     71250



##### <span style="color:MediumSlateBlue">Подбор гиперпараметров модели</span>

In [1818]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'service'
count_features = dict_spaces[feature_space]

# для работы функции corr_transform_to_force
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()

# настроим оптимизацию гипер параметров
def optuna_hgbc(trial):
  # задаем пространства поиска гиперпараметров
  learning_rate = trial.suggest_float('learning_rate',0.01,0.1)
  max_iter = trial.suggest_int('max_iter', 150, 250,step = 1)
  max_leaf_nodes = trial.suggest_int('max_leaf_nodes', 2, 60,step = 1)
  max_depth = trial.suggest_int('max_depth', 1, 10,step = 1)
  min_samples_leaf = trial.suggest_int('min_samples_leaf', 1, 60,step = 1)
  max_features = trial.suggest_float('max_features',0.6,1)
  l2_regularization = trial.suggest_float('l2_regularization',0.01,1)
  class_0_weight = trial.suggest_float('class_0_weight',0.01,1)
  class_1_weight = trial.suggest_float('class_1_weight',0.5,1)
  threshold = trial.suggest_float('threshold',0.7,1)
  class_1_percent = trial.suggest_float('class_1_percent',0.01,0.25)
  random_state = trial.suggest_int('random_state', 1, 1000000)

  # создаем модель
  optuna_gradient_boosting = HistGradientBoostingClassifier(
      learning_rate= learning_rate,
      max_iter = max_iter,
      max_leaf_nodes =max_leaf_nodes,
      max_depth = max_depth,
      min_samples_leaf = min_samples_leaf,
      max_features=max_features,
      l2_regularization = l2_regularization,
      class_weight={0:class_0_weight,1:class_1_weight},
      random_state=42)

  # с помощью функции corr_transform_to_force получим
  # список не коррелируемых признаков
  list_ncorr_features = corr_transform_to_force(corr_matrix,threshold=threshold)[1]

  # сформируем данные для анализа сбалансированности обучающих данных
  X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
  y_train_pd = pd.read_csv('target/target_train.csv')

  # поготовим данные y_train_pd к работе с функцией class_1_percent_samples
  y_train_pd.set_index('id',drop=False,inplace=True)

  # подготовим данные для обучения модели
  # с помощью функции class_1_percent_samples зададим долю 
  # класса 1
  list_c1_percent_id = class_1_percent_samples(y_train_pd,class_1_percent,random_state=random_state)[:1000000]

  # подготовим данные для обучения
  X_train_balanced = X_train_pd.loc[list_c1_percent_id]
  y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']

  # освободим память от "тяжелых" и ненужных файлов
  del X_train_pd, y_train_pd
  gc.collect()

  # я не воспользовался параметром timeout метода optimize потому, что  
  # optimize отставливает поиск параметров, если время обучения 
  # превышает timeout. Мне нужно чтобы поиск параметров продолжился.
  try:
    # для модуля func_time_out упакуем обучение модели в функцию try_func
    def try_func():
            return optuna_gradient_boosting.fit(X_train_balanced,y_train_balanced)
    # обучаем модель с ограничением по времени 10 минут (600 секунд)
    optuna_gradient_boosting = func_timeout.func_timeout(600, try_func)

    # удаляем крупные файлы чтобы высвободить память 
    del X_train_balanced, y_train_balanced
    gc.collect()

        # загружаем тестовые наборы
    # сформируем данные для анализа сбалансированности обучающих данных
    X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
    X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()[list_ncorr_features]
    y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
    y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()
    
    # делаем предсказание на обучающем и валидационном наборе и считаем метрики
    roc_train = metrics.roc_auc_score(y_train, optuna_gradient_boosting.predict_proba(X_train)[:,1])
    roc_valid = metrics.roc_auc_score(y_valid, optuna_gradient_boosting.predict_proba(X_valid)[:,1])
    f1_score = metrics.f1_score(y_valid, optuna_gradient_boosting.predict(X_valid))
    recall_1 = metrics.recall_score(y_valid, optuna_gradient_boosting.predict(X_valid),average=None,zero_division=0)[1]
    precision_1 = metrics.precision_score(y_valid, optuna_gradient_boosting.predict(X_valid),average=None,zero_division=0)[1]


    # удаляем крупные файлы чтобы высвободить память 
    del X_train, X_valid, y_train, y_valid
    gc.collect()

  except func_timeout.FunctionTimedOut:
    # удаляем крупные файлы чтобы высвободить память 
    del X_train_balanced, y_train_balanced
    gc.collect()
    
    # фиксируем пустые значения метрик
    roc_train = 0
    roc_valid = 0
    f1_score = 0
    recall_1 = 0
    precision_1 = 0
    pass

  return roc_train, roc_valid, f1_score, recall_1, precision_1

In [1819]:
# cоздаем объект исследования
# чтобы модель не переобучалась минимизируем roc_train 
# и максимизируем roc_valid
optuna_study_hgbc = optuna.create_study(study_name='HistGradientBoostingClassifier_'+feature_space+'_stat', 
                               directions=['maximize','maximize','maximize','maximize','maximize'], 
                               sampler=optuna.samplers.TPESampler(),
                               pruner='Hyperband',
                               storage='sqlite:///optuna_studies.db',
                               load_if_exists=True)

# ну случай удаления обучения
# optuna.delete_study(study_name='HistGradientBoostingClassifier'+feature_space+'_stat', storage='sqlite:///optuna_studies.db')

[I 2025-04-19 15:15:00,538] Using an existing study with name 'HistGradientBoostingClassifier_service_stat' instead of creating a new one.


In [1207]:
# ищем лучшую комбинацию гиперпараметров n_trials раз
optuna_study_hgbc.optimize(optuna_hgbc, n_trials=300)

[I 2025-04-18 09:37:18,290] Trial 0 finished with values: [0.638422673113314, 0.6354819152795661, 0.08919150705579666, 0.6855773072313224, 0.04769846564376251] and parameters: {'learning_rate': 0.031177619521820802, 'max_iter': 211, 'max_leaf_nodes': 8, 'max_depth': 7, 'min_samples_leaf': 8, 'max_features': 0.8815333436405937, 'l2_regularization': 0.10398204255760737, 'class_0_weight': 0.14023057775423087, 'class_1_weight': 0.5639393970133356, 'threshold': 0.7697414441428936, 'class_1_percent': 0.2173756690321168, 'random_state': 758128}.
[I 2025-04-18 09:37:27,293] Trial 1 finished with values: [0.6459965050551, 0.6401564199153431, 0.002380007933359778, 0.0011985617259288853, 0.16666666666666666] and parameters: {'learning_rate': 0.08267819323692287, 'max_iter': 231, 'max_leaf_nodes': 7, 'max_depth': 3, 'min_samples_leaf': 16, 'max_features': 0.7787976094513456, 'l2_regularization': 0.35002421661362204, 'class_0_weight': 0.422599850863065, 'class_1_weight': 0.6423585982585756, 'thresh

In [1820]:
# из полученного результат соврмируем Data Frame
optuna_study_hgbc_pd = optuna_study_hgbc.trials_dataframe()
# переименуем столбы
optuna_study_hgbc_pd.rename(columns={
    'values_0': 'roc_train',
    'values_1': 'roc_valid',
    'values_2': 'f1_score',
    'values_3': 'recall_1',
    'values_4': 'precision_1'
},inplace=True)
optuna_study_hgbc_pd.tail(5)

number  roc_train  roc_valid  f1_score  recall_1  precision_1  \
295     295   0.658287   0.641242  0.099141  0.536956     0.054612   
296     296   0.662682   0.641477  0.110810  0.351578     0.065770   
297     297   0.659675   0.641895  0.093336  0.091490     0.095258   
298     298   0.658903   0.640088  0.068801  0.989213     0.035640   
299     299   0.644104   0.639686  0.086370  0.076708     0.098816   

                datetime_start          datetime_complete  \
295 2025-04-18 10:27:33.709817 2025-04-18 10:27:47.540164   
296 2025-04-18 10:27:47.546356 2025-04-18 10:28:05.593301   
297 2025-04-18 10:28:05.598629 2025-04-18 10:28:28.424923   
298 2025-04-18 10:28:28.430985 2025-04-18 10:28:42.090501   
299 2025-04-18 10:28:42.096381 2025-04-18 10:28:56.364707   

                  duration  params_class_0_weight  ...  \
295 0 days 00:00:13.830347               0.071535  ...   
296 0 days 00:00:18.046945               0.111688  ...   
297 0 days 00:00:22.826294               0.091628  ...   
298 0 days 00:00:13.659516               0.023972  ...   
299 0 days 00:00:14.268326               0.130503  ...   

     params_l2_regularization  params_learning_rate  params_max_depth  \
295                  0.564126              0.094162                10   
296                  0.591157              0.035128                10   
297                  0.617937              0.019853                10   
298                  0.575163              0.089181                10   
299                  0.687720              0.086646                 3   

     params_max_features  params_max_iter  params_max_leaf_nodes  \
295             0.814409              247                     58   
296             0.929047              233                     56   
297             0.662309              235                     53   
298             0.942610              217                     59   
299             0.895121              242                     58   

     params_min_samples_leaf  params_random_state  params_threshold     state  
295                       56               356839          0.860727  COMPLETE  
296                       49               463020          0.911917  COMPLETE  
297                       55               419045          0.904984  COMPLETE  
298                       53                77388          0.921054  COMPLETE  
299                       45               385664          0.916070  COMPLETE  

[5 rows x 22 columns]

In [1821]:
# покаждем статистику обучения
print('Максимальное значение метрики ROC AUC на валидационном наборе:',round(optuna_study_hgbc_pd['roc_valid'].max(),3))
print('Среднее значение метрики ROC AUC на валидационном наборе:',round(optuna_study_hgbc_pd['roc_valid'].mean(),3))
print('Максимальное значение метрики f1_score на валидационном наборе:',round(optuna_study_hgbc_pd['f1_score'].max(),3))
print('Среднее значение метрики f1_score на валидационном наборе:',round(optuna_study_hgbc_pd['f1_score'].mean(),3))
print('Максимальное значение метрики recall_1 на валидационном наборе:',round(optuna_study_hgbc_pd['recall_1'].max(),3))
print('Среднее значение метрики recall_1 на валидационном наборе:',round(optuna_study_hgbc_pd['recall_1'].mean(),3))
print('Максимальное значение метрики precision_1 на валидационном наборе:',round(optuna_study_hgbc_pd['precision_1'].max(),3))
print('Среднее значение метрики precision_1 на валидационном наборе:',round(optuna_study_hgbc_pd['precision_1'].mean(),3))

Максимальное значение метрики ROC AUC на валидационном наборе: 0.644
Среднее значение метрики ROC AUC на валидационном наборе: 0.641
Максимальное значение метрики f1_score на валидационном наборе: 0.113
Среднее значение метрики f1_score на валидационном наборе: 0.078
Максимальное значение метрики recall_1 на валидационном наборе: 1.0
Среднее значение метрики recall_1 на валидационном наборе: 0.382
Максимальное значение метрики precision_1 на валидационном наборе: 1.0
Среднее значение метрики precision_1 на валидационном наборе: 0.087


In [1823]:
# Построим зависимость метрик качества модели от number

fig = px.scatter(
    data_frame=optuna_study_hgbc_pd[(optuna_study_hgbc_pd['roc_valid']>0.9999*optuna_study_hgbc_pd['roc_valid'].max())],
    x='number', #ось абсцисс
    y=['roc_train','roc_valid','recall_1','precision_1'], #ось ординат
)
fig.update_layout(
    title ={
        'text':'Зависимость качества модели от trials optuna', # Имя рабочей плоскости
        'font':{'size':35,'family':"Times New Roman"}, # размер и стиль написания имени рабочей плоскости
        'x':0.5, # Смешение имени по оси "x" на половину рабочей плоскости
        },
    height =800,# Высота рабочей плоскости
    width = 1350, # Ширина рабочей плоскости
    bargap=0.2, # Добавил расстояния между столбами гистограммы
    xaxis_title='trials optuna',
    yaxis_title='Величина параметра')
fig.update_xaxes(showspikes=True)
fig.update_yaxes(showspikes=True)

fig.show()

<span style="color:Blue">

Вывод:  

Их всех выбираем точку $number =69$.   
В этой точке оптимальные значения метрик $recall_1$ и $precision_1$, а  
также относительно высокая метрика $ROC AUC$.   
Посмотрим каким значениям гиперпараметров соотвествует выбранная точка.

In [1824]:
# определим номер лучшге варианта
best_optuna_number = 69

# сформируем словарь лучших гипирпарметров HistGradientBoostingClassifier
best_param_hgbc = {
    'learning_rate' : optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_learning_rate'].iloc[0],
    'max_iter' : optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_max_iter'].iloc[0],
    'max_leaf_nodes' : optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_max_leaf_nodes'].iloc[0],
    'max_depth' : optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_max_depth'].iloc[0],
    'min_samples_leaf' : optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_min_samples_leaf'].iloc[0],
    'max_features' : optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_max_features'].iloc[0],
    'l2_regularization' : optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_l2_regularization'].iloc[0],
    'class_weight' : {0: optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_class_0_weight'].iloc[0],
                      1: optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_class_1_weight'].iloc[0],}
    }

# определим перменные для лучших значений параметров
best_threshold = optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_threshold'].iloc[0]
best_class_1_percent = optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_class_1_percent'].iloc[0]
best_random_state = optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['params_random_state'].iloc[0]


# Выведем принятые наилучшие параметры
print('best learning rate:',round(best_param_hgbc['learning_rate'],3))
print('best max iter:',best_param_hgbc['max_iter'])
print('best max leaf nodes:',best_param_hgbc['max_leaf_nodes'])
print('best max depth:',best_param_hgbc['max_depth'])
print('best min samples leaf:',best_param_hgbc['min_samples_leaf'])
print('best max features:',round(best_param_hgbc['max_features'],3))
print('best l2 regularization:',round(best_param_hgbc['l2_regularization'],3))
print('best class 0 weight:',round(best_param_hgbc['class_weight'][0],3))
print('best class 1 weight:',round(best_param_hgbc['class_weight'][1],3))

print('best class 1 percent:',round(best_class_1_percent,3))
print('best threshold:',round(best_threshold,3))
print('time for best train:',round(optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['duration'].iloc[0].seconds/60),'minutes')

print()
print('ROC AUC на обучающем наборе:', round(optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['roc_train'].iloc[0],3))
print('ROC AUC на валидационном наборе:', round(optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['roc_valid'].iloc[0],3))
print('precision класса 1:', round(optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['precision_1'].iloc[0],3))
print('recall класса 1:', round(optuna_study_hgbc_pd[optuna_study_hgbc_pd['number']==best_optuna_number]['recall_1'].iloc[0],3))

best learning rate: 0.076
best max iter: 160
best max leaf nodes: 49
best max depth: 10
best min samples leaf: 38
best max features: 0.604
best l2 regularization: 0.831
best class 0 weight: 0.137
best class 1 weight: 0.581
best class 1 percent: 0.103
best threshold: 0.868
time for best train: 0 minutes

ROC AUC на обучающем наборе: 0.656
ROC AUC на валидационном наборе: 0.644
precision класса 1: 0.094
recall класса 1: 0.089


##### <span style="color:MediumSlateBlue">Обучение модели с лучшими параметрами</span>

In [1825]:
# определим прострастравсо признаков
dict_spaces = {
    'date' : 8,
    'late': 12,
    'credit': 4,
    'relative' : 6,
    'payments': 25,
    'service': 4}
feature_space = 'service'
count_features = dict_spaces[feature_space]

# для работы функции corr_transform_to_force
# подгрузим DataFrame с матрицей корреляции признаков
corr_matrix = fp.ParquetFile('features/base_models/stat/corr_matrix_'+feature_space).to_pandas()

# с помощью функции corr_transform_to_force получим
# список не коррелируемых признаков
list_ncorr_features = corr_transform_to_force(corr_matrix,threshold=best_threshold)[1]

# сформируем данные для анализа сбалансированности обучающих данных
X_train_pd = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
y_train_pd = pd.read_csv('target/target_train.csv')

# поготовим данные y_train_pd к работе с функцией class_1_percent_samples
y_train_pd.set_index('id',drop=False,inplace=True)

# подготовим данные для обучения модели
# с помощью функции class_1_percent_samples зададим долю 
# класса 1
list_c1_percent_id = class_1_percent_samples(y_train_pd,best_class_1_percent,random_state=best_random_state)[:1000000]

# подготовим данные для обучения
X_train_balanced = X_train_pd.loc[list_c1_percent_id]
y_train_balanced = y_train_pd.loc[list_c1_percent_id]['flag']

# освободим память от "тяжелых" и ненужных файлов
del X_train_pd, y_train_pd
gc.collect()

# обучаем модель HistGradientBoostingClassifier с наилучшеми параметрами
gradient_boosting = HistGradientBoostingClassifier(
        **best_param_hgbc,
        random_state=42)
gradient_boosting.fit(X_train_balanced,y_train_balanced)

# удаляем крупные файлы чтобы высвободить память 
del X_train_balanced, y_train_balanced
gc.collect()

# сформируем данные для анализа сбалансированности обучающих данных
X_train = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_train').to_pandas()[list_ncorr_features]
X_valid = fp.ParquetFile('features/base_models/stat/'+feature_space+'_stat_valid').to_pandas()[list_ncorr_features]
y_train = pd.read_csv('target/target_train.csv')['flag'].to_numpy()
y_valid = pd.read_csv('target/target_valid.csv')['flag'].to_numpy()

# делаем предсказание на обучающем и валидационном наборе и считаем метрики
y_train_gb_pred_proba = gradient_boosting.predict_proba(X_train)[:,1]
y_valid_gb_pred_proba = gradient_boosting.predict_proba(X_valid)[:,1]
y_valid_gb_pred = gradient_boosting.predict(X_valid)

# удаляем крупные файлы чтобы высвободить память 
del X_train, X_valid
gc.collect()

#Выводим значения метрик
print('ROC AUC на обучающем наборе', round(metrics.roc_auc_score(y_train, y_train_gb_pred_proba),3))
print('ROC AUC на валидационном наборе', round(metrics.roc_auc_score(y_valid, y_valid_gb_pred_proba),3))

print('Основные метрики на валидационом наборе:')
print(metrics.classification_report(y_valid,y_valid_gb_pred,zero_division=0))

# time: 1m 40s

ROC AUC на обучающем наборе 0.656
ROC AUC на валидационном наборе 0.644
Основные метрики на валидационом наборе:
              precision    recall  f1-score   support

           0       0.97      0.97      0.97     68747
           1       0.09      0.09      0.09      2503

    accuracy                           0.94     71250
   macro avg       0.53      0.53      0.53     71250
weighted avg       0.94      0.94      0.94     71250

